# Machine Learning Analyses: EEG-based Biomarkers of Social Emotions (Empathic Blame)

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

## Tutte e quattro le classi:

### 1 ) Baseline 2) Th resp 3) Pt Resp 4) Shared Resp

## STEP 1: salvare le stringhe delle paths in una lista di dizionari

## STEP 1: Funzioni Vecchie Terapisti e Pazienti

Sì, esatto. Con la logica attuale, le condizioni sperimentali potrebbero non corrispondere correttamente tra i dati dei terapisti e quelli dei pazienti. In particolare:

Nei **dati dei terapisti**

- la condizione "RespWindow_PhtResp_Th" viene categorizzata come "th_resp", mentre nei dati dei pazienti, la condizione corrispondente "RespWindow_PhtResp_Pt" viene categorizzata come "vision_resp". Questo può portare a una mancata corrispondenza nel conteggio dei dati per questa condizione.

Nei **dati dei pazienti** 

- la condizione "RespWindow_PtResp_Pt" viene categorizzata come "pt_resp", mentre nei dati dei terapisti, la condizione corrispondente "RespWindow_PtResp_Th" viene categorizzata come "vision_resp". Anche questo potrebbe creare una discrepanza.


## STEP 1.1: Nuova Funzione per TERAPISTI e PAZIENTI integrata

### Salvare le stringhe delle paths in una lista di dizionari dei dati dei TERAPISTI e PAZIENTI

Utilizzando questa funzione, i file vengono associati alle stesse condizioni sperimentali, come "th_resp" o "pt_resp," indipendentemente se il file si trova nella cartella "therapist" o "patient." 

In questo modo, puoi avere coppie di file che rappresentano la stessa condizione sperimentale per entrambe le categorie (terapisti e pazienti), e ciascuna coppia condividerà lo stesso codice comune di condizione (come "th_resp" o "pt_resp").

Questo approccio consente di accorpare in modo coerente i file relativi a una condizione sperimentale, rendendo possibile l'analisi congiunta dei dati provenienti da entrambe le categorie.


#### NOTA BENE

<br>

**IO**:  ok ora però vorrei chiederti una cosa.... quando faccio i print  di "list_dict_folder_paths_th" e "list_dict_folder_paths_pt" noto che la cartella HS03-HS04 viene stampata prima e la stessa cosa viene fatta per le condizioni sperimentali... voglio dire che 

la funzione dovrebbe considerare il valore crescente della cartella (HS01-HS02 è la prima ad esempio) e le path delle condizioni sperimentali da salvare vorrei che fossero anch'esse organizzate in modo che ci fosse prima la 'baseline', poi 'th_resp' poi 'pt_resp' e poi 'shared_resp'..

invece, nei print la loro posizione come chiave nel dizionario cambia dall'uno all'altro... quello che temo, è che questa diversa disorganizzqzione delle stringhe delle path dei file salvate dentro ogni dizionario poi posso creare dei problemi nei passaggi successivi.. può essere?

**CHATGPT**:

Sì, **la disorganizzazione delle chiavi nei dizionari può portare a problemi nei passaggi successivi, specialmente se ci si aspetta un certo ordine nelle chiavi**. 

In Python, i dizionari sono strutture di dati non ordinate fino alla versione 3.7, dove l'ordine di inserimento è mantenuto. 
Tuttavia, **è sempre una buona pratica garantire un ordine prevedibile, specialmente quando si ha a che fare con dati che devono seguire una sequenza specifica**.

Per garantire che le chiavi nel dizionario siano sempre ordinate in modo consistente, puoi utilizzare collections.OrderedDict o semplicemente costruire un nuovo dizionario in un ordine specifico dopo aver raccolto i file.

Ecco come potresti modificare la funzione per garantire che le chiavi siano sempre ordinate nel modo desiderato (cioè baseline, th_resp, pt_resp, shared_resp) e che le cartelle siano processate in ordine crescente:


### Implementazione: Salvare le stringhe delle paths in una lista di dizionari dei dati dei TERAPISTI e PAZIENTI

In [ ]:
'''
16 OTTOBRE: TERAPISTI CON ORDINAMENTO STRUTTURALE CHIAVI (i.e., CONDIZIONI SPERIMENTALI)

In questo codice:

Dopo aver costruito result_data, si ordina ciascun dizionario nella lista.

La funzione sorted() è usata con una chiave che ordina le chiavi del dizionario 
in base all'indice della categoria in category_order.

Viene restituita la lista di dizionari ordinati, dove
ogni dizionario ha le chiavi in ordine coerente con le categorie.

Questo approccio garantisce che l'ordine delle chiavi e dei file path sia sempre lo stesso,
semplificando l'elaborazione successiva.
'''

import os

def save_paths_file_edf_th(directory_path):
    
    # Verifica se la directory esiste
    if not os.path.exists(directory_path):
        print(f"La directory '{directory_path}' non esiste.")
        return

    # Lista di dizionari, uno per ogni cartella
    result_data = []

    # Contatore per tenere traccia delle cartelle
    folder_count = 1

    # Definizione dell'ordine delle categorie
    category_order = ["baseline", "th_resp", "pt_resp", "shared_resp"]

    # Naviga attraverso la directory e sottocartelle
    for root, dirs, files in os.walk(directory_path):
        
        '''
        Aggiungere la riga dirs.sort() all'interno del ciclo os.walk 
        ordinerà le directory in ordine alfabetico (o numerico, a seconda dei nomi) 
        prima che vengano esplorate. 
        Questo dovrebbe aiutarti a garantire che le cartelle vengano trattate nell'ordine desiderato.
        '''
        # Ordina le directory
        dirs.sort()  # Questa linea ordina le directory
        
        # Verifica se la directory corrente è "therapist"
        
        if "therapist" in root.split(os.sep):
            
            'OLD VERSION CON FILE EDF'
            # Verifica se il percorso corrente è una cartella e contiene file .edf
            #if any(file.endswith(".edf") for file in files):
            
            'MAT VERSION CON FILE .MAT'
            # Verifica se il percorso corrente è una cartella e contiene file .mat
            if any(file.endswith(".mat") for file in files):
                print(f"\033[1mEsplorazione della cartella\033[0m: \033[1m{root}\033[0m\n")
                
                # Dizionario per i percorsi dei file corrispondenti a ciascuna categoria nella cartella corrente
                file_paths = {}
                
                'OLD VERSION CON FILE EDF'
                # Filtra solo i file .edf
                #edf_files = [file for file in files if file.endswith(".edf")]
                
                # Filtra solo i file .mat
                'MAT VERSION CON FILE .MAT'
                
                mat_files = [file for file in files if file.endswith(".mat")]
                
                # Contatore per tenere traccia delle triplette
                count = 1
                
                'OLD VERSION CON FILE EDF'
                # Aggiungi i file al dizionario
                #for file in edf_files:
                
                'MAT VERSION CON FILE .MAT'
                # Aggiungi i file al dizionario
                for file in mat_files:
                    
                    file_path = os.path.join(root, file)

                    # Uniformiamo la logica di assegnazione delle categorie
                    if "RespWindow_NoResp_Th" in file_path:
                        category = "baseline"
                    elif "RespWindow_PhtResp_Th" in file_path:
                        category = "th_resp"
                    elif "RespWindow_PtResp_Th" in file_path:
                        category = "pt_resp"
                    elif "RespWindow_SharedResp_Th" in file_path:
                        category = "shared_resp"
                    else:
                        continue

                    # Assegna dinamicamente la chiave del dizionario in base alla categoria e al contatore delle cartelle
                    category_with_count = f"{category}_{folder_count}"

                    # Aggiungi il file_path al dizionario
                    file_paths[category_with_count] = file_path

                    print(f"\033[1mFile .edf trovato\033[0m: {file_path}")

                    # Incrementa il contatore per la successiva tripletta
                    count += 1

                    # Resetta il contatore a 1 ogni volta che raggiunge 4
                    if count > 4:
                        print(f"\nQUADRIPLETTA DI FILE .EDF SALVATA!")
                        print(f"SI RICOMINCIA CON NUOVA CARTELLA\n")
                        
                        # Incrementa il contatore delle cartelle
                        folder_count += 1

                        # Ripristina il contatore a 1
                        count = 1
                
                'OLD VERSION CON FILE EDF'
                # Aggiungi il dizionario corrente alla lista solo se ci sono file .edf
                #if any(file_path.endswith('.edf') for file_path in file_paths.values()):
                    
                'MAT VERSION CON FILE .MAT'
                # Aggiungi il dizionario corrente alla lista solo se ci sono file .mat
                if any(file_path.endswith('.mat') for file_path in file_paths.values()):
                    result_data.append(file_paths)

    # Ordina la lista di dizionari `result_data` in base all'ordine delle categorie
    sorted_result_data = []
    
    for file_paths in result_data:
        
        '''
        La parte 
        
        "key=lambda item: category_order.index('_'.join(item[0].split('_')[0:2])) 
        
        serve solo per determinare l'ordine delle chiavi, 
        ma non modifica effettivamente le chiavi stesse. 
        
        La funzione sorted() utilizza questa lambda per ottenere l'indice della categoria nella lista category_order 
        e ordinare le chiavi in base a questo indice.
        
        Le chiavi originali rimangono intatte nel dizionario ordinato.
        Quindi, se una chiave è ad esempio baseline_1, 
        sarà ordinata correttamente in base alla posizione di "baseline" nella lista category_order,
        ma il nome completo della chiave, cioè baseline_1, non verrà modificato o eliminato.
    
        Per gestire la differenza tra 
        la chiave "baseline" e 
        le altre chiavi che richiedono "th_resp", "pt_resp", e "shared_resp", 
        si implementa una logica condizionale nella funzione lambda 
        per determinare come estrarre la chiave corretta per il confronto. 
        
        La soluzione proposta segue questa logica:

        Se la chiave originale inizia con "baseline", estrai solo "baseline".
        Altrimenti, estrai le prime due parti della chiave per ottenere "th_resp", "pt_resp", o "shared_resp".
        '''
        
        # Crea un dizionario ordinato in base all'ordine delle categorie
        sorted_file_paths = dict(
            sorted(file_paths.items(),key=lambda item: category_order.index(
                item[0].split('_')[0] if item[0].startswith('baseline')
                else '_'.join(item[0].split('_')[0:2])
                )
            )
        )
        
        sorted_result_data.append(sorted_file_paths)
        
        # Estrai il numero del soggetto dalla prima chiave del dizionario ordinato
        subject_number = sorted_file_paths.keys().__iter__().__next__().split('_')[-1]

        # Stampa le chiavi ordinate per controllo
        print(f'\nChiavi ordinate per il \033[1msoggetto {subject_number}\033[0m:')
        for key in sorted_file_paths.keys():
            print(key)

    # Restituisci i dizionari ordinati ottenuti per ogni cartella
    return sorted_result_data

# Utilizzo della funzione

'''OLD DIRECTORY PER DATI CON ARTIFACT REJECTION SU BRAIN VISION ANALYZER'''
#directory = "/home/stefano/Interrogait/Dati_FSL_Sani/Filter_1_20/Familiari/"

'''NEW DIRECTORY CON EEG DATI ESTRATTI SU BRAIN VISION ANALYZER FINO A SEGMENTAZIONE PER CONDIZIONE SPERIMENTALE
+ SUCCESSIVA INTERPOLAZIONE/ARTIFACT REJECTION DEI DATI EEG SU MATLAB '''

directory = "/home/stefano/Interrogait/EEG_interpolated_1_45"


In [ ]:
list_dict_folder_paths_th = save_paths_file_edf_th(directory)

In [ ]:
'''TERAPISTI'''

#Lista di dizionari, ciascuno avente come chiave la condizione sperimentale, come valore la stringa della path 

print('La variabile "\033[1mlist_dict_folder_paths_th\033[0m" è : ', type(list_dict_folder_paths_th))
print()
print('Length di "\033[1mlist_dict_folder_paths_th\033[0m" è: ', len(list_dict_folder_paths_th))
print()
print('Gli \033[1melementi\033[0m della variabile "list_dict_folder_paths_th"  sono : ', type(list_dict_folder_paths_th[0]))
print()
print("\033[1mEsempio dell'elemento\033[0m: dizionario con chiavi  \n\n", list_dict_folder_paths_th[-1])

In [ ]:
# Stampa i dizionari ottenuti per ogni cartella
for idx, folder_dict in enumerate(list_dict_folder_paths_th):
    #print(f"Dizionario per le path dei files .edf della \033[1mcartella {idx + 1}\033[0m: \n\n{folder_dict}")
    #print()
    
    # Stampa solo le chiavi in grassetto
    print(f"Dictionary of \033[1msubject {idx}\033[0m: \n") 
    for key in folder_dict.keys():  # Rimuovi la virgola dopo 'key'
        value = folder_dict[key]  # Recupera il valore corrispondente alla chiave
        print(f"\033[1m{key}\033[0m: {value}")  # Stampa la chiave in grassetto
    
    print()  # Aggiunge una riga vuota dopo ogni dizionario

In [ ]:
'''
16 OTTOBRE: PAZIENTI SENZA ORDINAMENTO STRUTTURALI CHIAVI CONDIZIONI SPERIMENTALI

In questo codice:

Dopo aver costruito result_data, si ordina ciascun dizionario nella lista.

La funzione sorted() è usata con una chiave che ordina le chiavi del dizionario 
in base all'indice della categoria in category_order.

Viene restituita la lista di dizionari ordinati, dove
ogni dizionario ha le chiavi in ordine coerente con le categorie.

Questo approccio garantisce che l'ordine delle chiavi e dei file path sia sempre lo stesso,
semplificando l'elaborazione successiva.
'''

import os

def save_paths_file_edf_pt(directory_path):
    
    # Verifica se la directory esiste
    if not os.path.exists(directory_path):
        print(f"La directory '{directory_path}' non esiste.")
        return

    # Lista di dizionari, uno per ogni cartella
    result_data = []

    # Contatore per tenere traccia delle cartelle
    folder_count = 1

    # Definizione dell'ordine delle categorie
    category_order = ["baseline", "th_resp", "pt_resp", "shared_resp"]

    # Naviga attraverso la directory e sottocartelle
    for root, dirs, files in os.walk(directory_path):
        
        '''
        Aggiungere la riga dirs.sort() all'interno del ciclo os.walk 
        ordinerà le directory in ordine alfabetico (o numerico, a seconda dei nomi) 
        prima che vengano esplorate. 
        Questo dovrebbe aiutarti a garantire che le cartelle vengano trattate nell'ordine desiderato.
        '''
        # Ordina le directory
        dirs.sort()  # Questa linea ordina le directory
        
        # Verifica se la directory corrente è "therapist"
        
        if "patient" in root.split(os.sep):
            
            'OLD VERSION CON FILE EDF'
            # Verifica se il percorso corrente è una cartella e contiene file .edf
            #if any(file.endswith(".edf") for file in files):
            
            'MAT VERSION CON FILE .MAT'
            # Verifica se il percorso corrente è una cartella e contiene file .mat
            if any(file.endswith(".mat") for file in files):
                print(f"\033[1mEsplorazione della cartella\033[0m: \033[1m{root}\033[0m\n")
                
                # Dizionario per i percorsi dei file corrispondenti a ciascuna categoria nella cartella corrente
                file_paths = {}
                
                'OLD VERSION CON FILE EDF'
                # Filtra solo i file .edf
                #edf_files = [file for file in files if file.endswith(".edf")]
                
                # Filtra solo i file .mat
                'MAT VERSION CON FILE .MAT'
                
                mat_files = [file for file in files if file.endswith(".mat")]
                
                # Contatore per tenere traccia delle triplette
                count = 1
                
                'OLD VERSION CON FILE EDF'
                # Aggiungi i file al dizionario
                #for file in edf_files:
                
                'MAT VERSION CON FILE .MAT'
                # Aggiungi i file al dizionario
                for file in mat_files:
                    
                    file_path = os.path.join(root, file)

                    # Uniformiamo la logica di assegnazione delle categorie
                    if "RespWindow_NoResp_Pt" in file_path:
                        category = "baseline"
                    elif "RespWindow_PhtResp_Pt" in file_path:
                        category = "th_resp"
                    elif "RespWindow_PtResp_Pt" in file_path:
                        category = "pt_resp"
                    elif "RespWindow_SharedResp_Pt" in file_path:
                        category = "shared_resp"
                    else:
                        continue

                    # Assegna dinamicamente la chiave del dizionario in base alla categoria e al contatore delle cartelle
                    category_with_count = f"{category}_{folder_count}"

                    # Aggiungi il file_path al dizionario
                    file_paths[category_with_count] = file_path

                    print(f"\033[1mFile .edf trovato\033[0m: {file_path}")

                    # Incrementa il contatore per la successiva tripletta
                    count += 1

                    # Resetta il contatore a 1 ogni volta che raggiunge 4
                    if count > 4:
                        print(f"\nQUADRIPLETTA DI FILE .EDF SALVATA!")
                        print(f"SI RICOMINCIA CON NUOVA CARTELLA\n")
                        
                        # Incrementa il contatore delle cartelle
                        folder_count += 1

                        # Ripristina il contatore a 1
                        count = 1
                
                'OLD VERSION CON FILE EDF'
                # Aggiungi il dizionario corrente alla lista solo se ci sono file .edf
                #if any(file_path.endswith('.edf') for file_path in file_paths.values()):
                    
                'MAT VERSION CON FILE .MAT'
                # Aggiungi il dizionario corrente alla lista solo se ci sono file .mat
                if any(file_path.endswith('.mat') for file_path in file_paths.values()):
                    result_data.append(file_paths)

    # Ordina la lista di dizionari `result_data` in base all'ordine delle categorie
    sorted_result_data = []
    
    for file_paths in result_data:
        
        '''
        La parte 
        
        "key=lambda item: category_order.index('_'.join(item[0].split('_')[0:2])) 
        
        serve solo per determinare l'ordine delle chiavi, 
        ma non modifica effettivamente le chiavi stesse. 
        
        La funzione sorted() utilizza questa lambda per ottenere l'indice della categoria nella lista category_order 
        e ordinare le chiavi in base a questo indice.
        
        Le chiavi originali rimangono intatte nel dizionario ordinato.
        Quindi, se una chiave è ad esempio baseline_1, 
        sarà ordinata correttamente in base alla posizione di "baseline" nella lista category_order,
        ma il nome completo della chiave, cioè baseline_1, non verrà modificato o eliminato.
    
        Per gestire la differenza tra 
        la chiave "baseline" e 
        le altre chiavi che richiedono "th_resp", "pt_resp", e "shared_resp", 
        si implementa una logica condizionale nella funzione lambda 
        per determinare come estrarre la chiave corretta per il confronto. 
        
        La soluzione proposta segue questa logica:

        Se la chiave originale inizia con "baseline", estrai solo "baseline".
        Altrimenti, estrai le prime due parti della chiave per ottenere "th_resp", "pt_resp", o "shared_resp".
        '''
        
        # Crea un dizionario ordinato in base all'ordine delle categorie
        sorted_file_paths = dict(
            sorted(file_paths.items(),key=lambda item: category_order.index(
                item[0].split('_')[0] if item[0].startswith('baseline')
                else '_'.join(item[0].split('_')[0:2])
                )
            )
        )
        
        sorted_result_data.append(sorted_file_paths)
        
        # Estrai il numero del soggetto dalla prima chiave del dizionario ordinato
        subject_number = sorted_file_paths.keys().__iter__().__next__().split('_')[-1]

        # Stampa le chiavi ordinate per controllo
        print(f'\nChiavi ordinate per il \033[1msoggetto {subject_number}\033[0m:')
        for key in sorted_file_paths.keys():
            print(key)

    # Restituisci i dizionari ordinati ottenuti per ogni cartella
    return sorted_result_data

# Utilizzo della funzione

'''OLD DIRECTORY PER DATI CON ARTIFACT REJECTION SU BRAIN VISION ANALYZER'''
#directory = "/home/stefano/Interrogait/Dati_FSL_Sani/Filter_1_20/Familiari/"

'''NEW DIRECTORY CON EEG DATI ESTRATTI SU BRAIN VISION ANALYZER FINO A SEGMENTAZIONE PER CONDIZIONE SPERIMENTALE
+ SUCCESSIVA INTERPOLAZIONE/ARTIFACT REJECTION DEI DATI EEG SU MATLAB '''

directory = "/home/stefano/Interrogait/EEG_interpolated_1_45"


In [ ]:
list_dict_folder_paths_pt = save_paths_file_edf_pt(directory)

In [ ]:
'''PAZIENTI'''

#Lista di dizionari, ciascuno avento come chiave la condizione sperimentale, come valore la stringa della path 

print('La variabile "\033[1mlist_dict_folder_paths_pt\033[0m" è : ', type(list_dict_folder_paths_pt))
print()
print('Length di "\033[1mlist_dict_folder_paths_pt\033[0m" è: ', len(list_dict_folder_paths_pt))
print()
print('Gli \033[1melementi\033[0m della variabile "list_dict_folder_paths_pt"  sono : ', type(list_dict_folder_paths_pt[0]))
print()
print("\033[1mEsempio dell'elemento\033[0m: dizionario con chiavi  \n\n", list_dict_folder_paths_pt[-1])

In [ ]:
# Stampa i dizionari ottenuti per ogni cartella
for idx, folder_dict in enumerate(list_dict_folder_paths_pt):
    #print(f"Dizionario per le path dei files .edf della \033[1mcartella {idx + 1}\033[0m: \n\n{folder_dict}")
    #print()
    
    # Stampa solo le chiavi in grassetto
    print(f"Dictionary of \033[1msubject {idx}\033[0m: \n") 
    for key in folder_dict.keys():  # Rimuovi la virgola dopo 'key'
        value = folder_dict[key]  # Recupera il valore corrispondente alla chiave
        print(f"\033[1m{key}\033[0m: {value}")  # Stampa la chiave in grassetto
    
    print()  # Aggiunge una riga vuota dopo ogni dizionario

## STEP 2: caricare file raw edf dalla lista di dizionari delle paths


## STEP 2.1: caricare file raw edf dalla lista di dizionari delle paths dei TERAPISTI


Files per il quale compare il warning...


Extracting EDF parameters from /home/stefano/Interrogait/Dati_FSL_Sani/Filter_1_20/Familiari/HS11_HS12/therapist/**HS11_HS12_EEG_Task_Hyper_RespWindow_SharedResp_Th_edf.edf...**
EDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 16499  =      0.000 ...    65.996 secs...
/tmp/ipykernel_32815/2240037324.py:38: RuntimeWarning: Number of records from the header does not match the file size (perhaps the recording was not stopped before exiting). Inferring from the file size.
  raw_eeg = mne.io.read_raw_edf(file_path, preload=True)


Extracting EDF parameters from /home/stefano/Interrogait/Dati_FSL_Sani/Filter_1_20/Familiari/HS23_HS24/therapist/**HS23_HS24_EEG_Task_Hyper_RespWindow_NoResp_Th_edf.edf...**
EDF file detected
Setting channel info structure...
Creating raw.info structure...
/tmp/ipykernel_32815/2240037324.py:38: RuntimeWarning: Number of records from the header does not match the file size (perhaps the recording was not stopped before exiting). Inferring from the file size.
  raw_eeg = mne.io.read_raw_edf(file_path, preload=True)


Extracting EDF parameters from /home/stefano/Interrogait/Dati_FSL_Sani/Filter_1_20/Familiari/HS27_HS28/therapist/**HS27_HS28_EEG_Task_Hyper_RespWindow_PtResp_Th_edf.edf...**
EDF file detected
Setting channel info structure...
Creating raw.info structure...
/tmp/ipykernel_32815/2240037324.py:38: RuntimeWarning: Number of records from the header does not match the file size (perhaps the recording was not stopped before exiting). Inferring from the file size.
  raw_eeg = mne.io.read_raw_edf(file_path, preload=True)

che vuol dire in sostanza, che il file non veine correttamente letto..?



In [ ]:
def create_couple_dict_th(paths_list): 
    result_list = []

    for original_dict in paths_list:
        
        # Estrai la chiave dal dizionario
        first_key = list(original_dict.keys())[0]

        # Trova la parte numerica della chiave
        numeric_part = ''.join(filter(str.isdigit, first_key))

        #print(numeric_part)

        # Controlla la lunghezza della parte numerica

        # Se la parte numerica è maggiore di 1, allora prendi tutti i valori numerici 
        if len(numeric_part) > 1:
            coppia_key = first_key[-len(numeric_part):]  # Prendi gli ultimi n caratteri
            #print(f"coppia_key se length è maggiore di 1: {coppia_key}")
            
        # Altrimenti, prendi solo l'ultimo carattere se la parte numerica è lunga 1    
        else:
            coppia_key = first_key[-1]  
            #print(f"coppia_key se length è uguale 1: {coppia_key}")
       
        nome_coppia = 'coppia' 
        
        # Crea il nome dinamico del dizionario
        coppia = nome_coppia + f"_" + coppia_key
        #print(coppia)

        # Crea il dizionario con il nome dinamico
        result_dict = {coppia: {}}

        for category, file_path in original_dict.items():
            
            '''OLD VERSION - PER CARICARE I FILE .EDF CON MNE PYTHON'''
            # Leggi il file raw EEG
            #raw_eeg = mne.io.read_raw_edf(file_path, preload=True)

            '''NEW VERSION - PER CARICARE I FILE .MAT CON SCIPY PYTHON -version 1-10.1'''
            # Leggi il file raw EEG
            #https://docs.scipy.org/doc/scipy/reference/generated/scipy.io.loadmat.html --version 1.10.1
            
            raw_eeg = scipy.io.loadmat(file_path, simplify_cells = True)
            
            # Aggiungi la coppia al nuovo dizionario con il nome della categoria come chiave
            result_dict[coppia][category]= raw_eeg

        result_list.append(result_dict)
    
    return result_list


In [ ]:
couple_dict_edf_th = create_couple_dict_th(list_dict_folder_paths_th)

In [ ]:
couple_dict_edf_th[0]['coppia_1']['baseline_1']['EEG'].keys()

In [ ]:
couple_dict_edf_th[0]['coppia_1']['baseline_1']['EEG']['samp'].shape
#couple_dict_edf_th[0]['coppia_1']['baseline_1']['EEG'].keys()

In [ ]:
#couple_dict_edf_th[0]['coppia_1']['baseline_1']['EEG'].keys()

#dict_keys(['label', 'valid', 'fSamp', 'trigger', 'period', 'datatype', 'task', 'samp', 'ArtTab', 'TrRej', 'interp'])

In [ ]:
'''
#La struttura dati è una lista di dizionari, dove ogni dizionario ha una chiave dinamica (come 'coppia_1') e come valore un altro dizionario. 

#Quest'ultimo dizionario ha

#come chiavi le categorie ('shared_resp_1', 'th_resp_1', 'baseline_1') e come valore
#come valore un altro dizionario con la chiave 'raw_EEG' associata a un oggetto RawEDF
    
#In questo modo, hai una gerarchia di dizionari e sottodizionari per organizzare le informazioni
'''

# Stampa nuovi dizionari per coppia con sotto-chiavi delle condizioni
for idx, coppia_dict in enumerate(couple_dict_edf_th):
    print(f"\033[1mDizionario {idx + 1}\033[0m: \n{coppia_dict}")
    print()

In [ ]:
# Creazione copie della struttura di lista di dizionari
import copy 
couple_dict_data_th = cp.deepcopy(couple_dict_edf_th)
print('Length della Lista di Dizionari delle Coppie (i.e., couple_dict_data): ', len(couple_dict_data_th))

## STEP 2.2: caricare file raw edf dalla lista di dizionari delle paths dei PAZIENTI

In [ ]:
def create_couple_dict_pt(paths_list): 
    result_list = []

    for original_dict in paths_list:
        
        # Estrai la chiave dal dizionario
        first_key = list(original_dict.keys())[0]

        # Trova la parte numerica della chiave
        numeric_part = ''.join(filter(str.isdigit, first_key))

        #print(numeric_part)

        # Controlla la lunghezza della parte numerica

        # Se la parte numerica è maggiore di 1, allora prendi tutti i valori numerici 
        if len(numeric_part) > 1:
            coppia_key = first_key[-len(numeric_part):]  # Prendi gli ultimi n caratteri
            #print(f"coppia_key se length è maggiore di 1: {coppia_key}")
            
        # Altrimenti, prendi solo l'ultimo carattere se la parte numerica è lunga 1    
        else:
            coppia_key = first_key[-1]  
            #print(f"coppia_key se length è uguale 1: {coppia_key}")
       
        nome_coppia = 'coppia' 
        
        # Crea il nome dinamico del dizionario
        coppia = nome_coppia + f"_" + coppia_key
        #print(coppia)

        # Crea il dizionario con il nome dinamico
        result_dict = {coppia: {}}

        for category, file_path in original_dict.items():
            
            '''OLD VERSION - PER CARICARE I FILE .EDF CON MNE PYTHON'''
            # Leggi il file raw EEG
            #raw_eeg = mne.io.read_raw_edf(file_path, preload=True)

            '''NEW VERSION - PER CARICARE I FILE .MAT CON SCIPY PYTHON -version 1-10.1'''
            # Leggi il file raw EEG
            #https://docs.scipy.org/doc/scipy/reference/generated/scipy.io.loadmat.html --version 1.10.1
            
            raw_eeg = scipy.io.loadmat(file_path, simplify_cells = True)
            
            # Aggiungi la coppia al nuovo dizionario con il nome della categoria come chiave
            result_dict[coppia][category]= raw_eeg

        result_list.append(result_dict)
    
    return result_list


In [ ]:
couple_dict_edf_pt = create_couple_dict_pt(list_dict_folder_paths_pt)

In [ ]:
'''
#La struttura dati è una lista di dizionari, dove ogni dizionario ha una chiave dinamica (come 'coppia_1') e come valore un altro dizionario. 

#Quest'ultimo dizionario ha

#come chiavi le categorie ('shared_resp_1', 'th_resp_1', 'baseline_1') e come valore
#come valore un altro dizionario con la chiave 'raw_EEG' associata a un oggetto RawEDF
    
#In questo modo, hai una gerarchia di dizionari e sottodizionari per organizzare le informazioni
'''

# Stampa nuovi dizionari per coppia con sotto-chiavi delle condizioni
for idx, coppia_dict in enumerate(couple_dict_edf_pt):
    print(f"\033[1mDizionario {idx + 1}\033[0m: \n{coppia_dict}")
    print()

In [ ]:
# Creazione copie della struttura di lista di dizionari
import copy 
couple_dict_data_pt = cp.deepcopy(couple_dict_edf_pt)
print('Length della Lista di Dizionari delle Coppie (i.e., couple_dict_data): ', len(couple_dict_data_pt))

## STEP 2.3: Calcolo dei Campioni Temporali e Secondi Registrati per la I-ESIMA COPPIA TERAPISTA-PAZIENTE

In [ ]:
import mne

# Assumiamo che couple_dict_data_th e couple_dict_data_pt siano già stati definiti

# Dizionario per memorizzare le discrepanze
discrepancies = {}

# Itera attraverso le coppie di terapeuti e pazienti
for idx in range(len(couple_dict_data_th)):
    therapist_dict = couple_dict_data_th[idx]
    patient_dict = couple_dict_data_pt[idx]
    
    therapist_key = list(therapist_dict.keys())[0]
    patient_key = list(patient_dict.keys())[0]

    #print(f"\nComparing data for {therapist_key} and {patient_key}:")

    # Itera attraverso le condizioni sperimentali nel dizionario del terapista
    for condition in therapist_dict[therapist_key].keys():
        therapist_raw_eeg = therapist_dict[therapist_key][condition]
        
        # Estrai n_times e durata in secondi
        n_times_therapist = therapist_raw_eeg.n_times
        duration_therapist = n_times_therapist / therapist_raw_eeg.info['sfreq']  # in secondi

        # Trova la condizione corrispondente nel dizionario del paziente
        if condition in patient_dict[patient_key]:
            patient_raw_eeg = patient_dict[patient_key][condition]
            n_times_patient = patient_raw_eeg.n_times
            duration_patient = n_times_patient / patient_raw_eeg.info['sfreq']  # in secondi
            
            # Stampa le informazioni
            #print(f"\nCondition: {condition}")
            #print(f"\tTherapist - n_times: {n_times_therapist}, Duration: {duration_therapist:.2f} s")  # in secondi
            #print(f"\tPatient - n_times: {n_times_patient}, Duration: {duration_patient:.2f} s")  # in secondi
            
            # Controlla le discrepanze
            if n_times_therapist != n_times_patient or duration_therapist != duration_patient:
                discrepancies[condition] = {
                    'therapist': {
                        'n_times': n_times_therapist,
                        'duration': duration_therapist
                    },
                    'patient': {
                        'n_times': n_times_patient,
                        'duration': duration_patient
                    }
                }
        else:
            print(f"\nCondition '{condition}' not found for {patient_key}.")

# Stampa le discrepanze trovate
if discrepancies:
    print("\nDiscrepancies found:")
    for condition, details in discrepancies.items():
        print(f"\n\033[1mCondition: {condition}\033[0m")
        print(f"\tTherapist - n_times: {details['therapist']['n_times']}, Duration: {details['therapist']['duration']:.2f} s")
        print(f"\tPatient - n_times: {details['patient']['n_times']}, Duration: {details['patient']['duration']:.2f} s")
else:
    print("\nNo discrepancies found.")


## STEP 3: conversione dati in array numpy, estrazione n° label e creazione finestre EEG

### STEP 3.1: conversione dati in array numpy, estrazione n° label e creazione finestre EEG dei TERAPISTI

In [ ]:
#FUNZIONE PER 
# 1) CONVERTIRE FILE RAW EDF IN NUMPY ARRAY 
# 2) CREARE DELLE LABEL ASSOCIATE AL N° DI SEGMENTI DA CONSIDERARE PER LE CONDIZIONI 
# 3) SCOMPONGO IL DATO EEG IN EPOCHE IN MODO DA PREPARARLE PER CLASSIFICATORE

    # 1° DIMENSIONE: N° LABEL PER FINESTRA 
    # 2° DIMENSIONE: N° CANALI
    # 3° DIMENSIONE: N° FINESTRE EEG


''' 

                                    OLD APPROACH PER FILE EDF
Estraggo il n° di campioni per ogni file EDF e lo divido per la frequenza di campionamento (250Hz) * segmentazione finestra (1.2 sec) 
in modo da ottenere il valore numerico della divisione, che arrotondo per creare un n° di labels corrispondenti
per la specifica condizione sperimentale. 

Alla fine, converto i file raw_edf in numpy array e li organizzo per finestrature da 300 campioni, 

'''


'''
                                    NEW APPROACH PER FILE MAT

Estraggo i trial EEG di ogni soggetto per ogni coppia di ogni condizione sperimentale,
inverto le shape (dimensioni) dei miei file .mat originari da 

                        (n_time_points, n_channels, n_trials) 
                                         a
                        (n_trials, n_channels, n_time_points) 

Creo un n° di labels pari al n° di trials della condizione corrente per il soggetto corrente
'''

def prepare_data_and_labels_th(couple_dict):
    
    # Creare una copia profonda del dizionario di coppie
    couple_dict_copy = cp.deepcopy(couple_dict)
    
    for individual_couple in couple_dict_copy:
        
        # Creare una copia delle chiavi per evitare RuntimeError
        keys_copy = list(individual_couple.keys())
        
        # Print(f'keys_copy is :, {keys_copy},\n\n')

        # Per ogni elemento della copia delle chiavi del sotto-dizionario (della specifica coppia)
        for coppia_key in keys_copy:
            
            print(f'\n\033[1mProcessing couple key\033[0m: \033[1m{coppia_key}\033[0m')
            
            condition_value = individual_couple[coppia_key]
            
            # Creare una copia delle chiavi per evitare RuntimeError
            condition_keys_copy = list(condition_value.keys())
            
            # print(f'condition_keys_copy is :, {condition_keys_copy},\n\n')
            
            for condition_key in condition_keys_copy:
                
                print(f'\nProcessing condition key: \033[1m{condition_key}\033[0m\n')
                
                '''VECCHIA VERSIONE PER FILE EDF'''
                # Estrarre i dati EEG
                #raw_eeg_value = condition_value[condition_key]
                
                '''NUOVA VERSIONE PER FILE .MAT'''
                # Estrarre i dati EEG
                raw_eeg_value = condition_value[condition_key]['EEG']['samp']
                
                '''VECCHIA VERSIONE PER FILE EDF'''
                # 1. Per ogni file raw, estrarre il numero di campioni temporali EEG.
                #n_times = raw_eeg_value.n_times
                #print(f'n_times: {n_times}')
                
                '''NUOVA VERSIONE PER FILE .MAT'''
                 # Invertire la shape dei dati:    
                #da (n_time_points, channels, trials) a (trials, channels, n_time_points)
                
                raw_eeg_value = np.transpose(raw_eeg_value, (2, 1, 0))
                
                print(f'EEG trials shape \033[1m{raw_eeg_value.shape}\033[0m')
                
                '''VECCHIA VERSIONE PER FILE EDF'''
                # 2. Calcolare il numero di etichette (labels) da inserire.
                #labels_num = math.floor(n_times / (250 * 1.2))
                
                #max_labels_num = n_times / (250 * 1.2)
                #print(f"max_labels_num would be \033[1m{max_labels_num}\033[0m")
                #print(f'labels_num: {labels_num}')
                
                '''NUOVA VERSIONE PER FILE .MAT'''
                # Calcolare il numero di etichette (labels) come il numero di trials
                labels_num = raw_eeg_value.shape[0]
                print(f'Number of labels (trials): \033[1m{labels_num}\033[0m')
                
                # 3. Utilizzare un'istruzione condizionale per assegnare valori alle etichette.
                if 'baseline' in condition_key:
                    labels_key = f'{condition_key}_labels'
                    condition_value[labels_key] = ['0'] * labels_num
                elif 'th_resp' in condition_key:
                    labels_key = f'{condition_key}_labels'
                    condition_value[labels_key] = ['1'] * labels_num
                elif 'pt_resp' in condition_key:
                    labels_key = f'{condition_key}_labels'
                    condition_value[labels_key] = ['2'] * labels_num
                elif 'shared_resp' in condition_key:
                    labels_key = f'{condition_key}_labels'
                    condition_value[labels_key] = ['3'] * labels_num
                
                '''VECCHIA VERSIONE PER FILE EDF'''
                # 4. Sovrascrivi direttamente il raw_edf con l'array NumPy
                #condition_value[condition_key] = raw_eeg_value.get_data()
                
                '''NUOVA VERSIONE PER FILE .MAT'''
                # Sovrascrivere il dizionario con i dati invertiti
                condition_value[condition_key] = raw_eeg_value
                
                '''VECCHIA VERSIONE PER FILE EDF'''
                #Divido il segnale EEG per ogni label 

                #EEG_windows = list()
                #for i in range(labels_num):
                #    window_data = condition_value[condition_key][:, i*300:(i+1)*300]
                #    EEG_windows.append(window_data)
        
                #print(len(EEG_windows))
                
                #condition_value[condition_key] = np.array(EEG_windows)
                #print(f"The shape of the current EEG_data is: \033[1m{condition_value[condition_key].shape}\033[0m")

    return couple_dict_copy


In [ ]:
# Usa la funzione per convertire i dati e aggiungere le labels
dataset_updated_th = prepare_data_and_labels_th(couple_dict_data_th)

In [ ]:
# STAMPO IL TIPO DELLA VARIABILE CHE CONTIENE OGNI DIZIONARIO PER LE COPPIE CON DENTRO I RELATIVI DIZIONARI DEI DATI E LABEL
print(f"dataset_updated_th is: \033[1m{type(dataset_updated_th)}\033[0m")
print()
print(f"Gli elementi della variabile dataset_updated_th sono : \033[1m{type(dataset_updated_th[0])}\033[0m")
print()
print(f"Esempio dell'elemento: dizionario con chiavi  \n\n {dataset_updated_th[0]}")

In [ ]:
# STAMPO LE CHIAVI DI CIASCUN SOTTODIZIONARIO DENTRO LA LISTA DI DIZIONARI
for individual_couple, el in enumerate (dataset_updated_th):
    for id_dict in el:
        print(el[id_dict].keys())

### STEP 3.2: conversione dati in array numpy, estrazione n° label e creazione finestre EEG dei PAZIENTI

In [ ]:
#FUNZIONE PER 
# 1) CONVERTIRE FILE RAW EDF IN NUMPY ARRAY 
# 2) CREARE DELLE LABEL ASSOCIATE AL N° DI SEGMENTI DA CONSIDERARE PER LE CONDIZIONI 
# 3) SCOMPONGO IL DATO EEG IN EPOCHE IN MODO DA PREPARARLE PER CLASSIFICATORE

    # 1° DIMENSIONE: N° LABEL PER FINESTRA 
    # 2° DIMENSIONE: N° CANALI
    # 3° DIMENSIONE: N° FINESTRE EEG


''' 

                                    OLD APPROACH PER FILE EDF
Estraggo il n° di campioni per ogni file EDF e lo divido per la frequenza di campionamento (250Hz) * segmentazione finestra (1.2 sec) 
in modo da ottenere il valore numerico della divisione, che arrotondo per creare un n° di labels corrispondenti
per la specifica condizione sperimentale. 

Alla fine, converto i file raw_edf in numpy array e li organizzo per finestrature da 300 campioni, 

'''


'''
                                    NEW APPROACH PER FILE MAT

Estraggo i trial EEG di ogni soggetto per ogni coppia di ogni condizione sperimentale,
inverto le shape (dimensioni) dei miei file .mat originari da 

                        (n_time_points, n_channels, n_trials) 
                                         a
                        (n_trials, n_channels, n_time_points) 

Creo un n° di labels pari al n° di trials della condizione corrente per il soggetto corrente
'''

def prepare_data_and_labels_pt(couple_dict):
    
    # Creare una copia profonda del dizionario di coppie
    couple_dict_copy = cp.deepcopy(couple_dict)
    
    for individual_couple in couple_dict_copy:
        
        # Creare una copia delle chiavi per evitare RuntimeError
        keys_copy = list(individual_couple.keys())
        
        # Print(f'keys_copy is :, {keys_copy},\n\n')

        # Per ogni elemento della copia delle chiavi del sotto-dizionario (della specifica coppia)
        for coppia_key in keys_copy:
            
            print(f'\n\033[1mProcessing couple key\033[0m: \033[1m{coppia_key}\033[0m')
            
            condition_value = individual_couple[coppia_key]
            
            # Creare una copia delle chiavi per evitare RuntimeError
            condition_keys_copy = list(condition_value.keys())
            
            # print(f'condition_keys_copy is :, {condition_keys_copy},\n\n')
            
            for condition_key in condition_keys_copy:
                
                print(f'\nProcessing condition key: \033[1m{condition_key}\033[0m\n')
                
                '''VECCHIA VERSIONE PER FILE EDF'''
                # Estrarre i dati EEG
                #raw_eeg_value = condition_value[condition_key]
                
                '''NUOVA VERSIONE PER FILE .MAT'''
                # Estrarre i dati EEG
                raw_eeg_value = condition_value[condition_key]['EEG']['samp']
                
                '''VECCHIA VERSIONE PER FILE EDF'''
                # 1. Per ogni file raw, estrarre il numero di campioni temporali EEG.
                #n_times = raw_eeg_value.n_times
                #print(f'n_times: {n_times}')
                
                '''NUOVA VERSIONE PER FILE .MAT'''
                 # Invertire la shape dei dati:    
                #da (n_time_points, channels, trials) a (trials, channels, n_time_points)
                
                raw_eeg_value = np.transpose(raw_eeg_value, (2, 1, 0))
                
                print(f'EEG trials shape \033[1m{raw_eeg_value.shape}\033[0m')
                
                '''VECCHIA VERSIONE PER FILE EDF'''
                # 2. Calcolare il numero di etichette (labels) da inserire.
                #labels_num = math.floor(n_times / (250 * 1.2))
                
                #max_labels_num = n_times / (250 * 1.2)
                #print(f"max_labels_num would be \033[1m{max_labels_num}\033[0m")
                #print(f'labels_num: {labels_num}')
                
                '''NUOVA VERSIONE PER FILE .MAT'''
                # Calcolare il numero di etichette (labels) come il numero di trials
                labels_num = raw_eeg_value.shape[0]
                print(f'Number of labels (trials): \033[1m{labels_num}\033[0m')
                
                # 3. Utilizzare un'istruzione condizionale per assegnare valori alle etichette.
                if 'baseline' in condition_key:
                    labels_key = f'{condition_key}_labels'
                    condition_value[labels_key] = ['0'] * labels_num
                elif 'th_resp' in condition_key:
                    labels_key = f'{condition_key}_labels'
                    condition_value[labels_key] = ['1'] * labels_num
                elif 'pt_resp' in condition_key:
                    labels_key = f'{condition_key}_labels'
                    condition_value[labels_key] = ['2'] * labels_num
                elif 'shared_resp' in condition_key:
                    labels_key = f'{condition_key}_labels'
                    condition_value[labels_key] = ['3'] * labels_num
                
                '''VECCHIA VERSIONE PER FILE EDF'''
                # 4. Sovrascrivi direttamente il raw_edf con l'array NumPy
                #condition_value[condition_key] = raw_eeg_value.get_data()
                
                '''NUOVA VERSIONE PER FILE .MAT'''
                # Sovrascrivere il dizionario con i dati invertiti
                condition_value[condition_key] = raw_eeg_value
                
                '''VECCHIA VERSIONE PER FILE EDF'''
                #Divido il segnale EEG per ogni label 

                #EEG_windows = list()
                #for i in range(labels_num):
                #    window_data = condition_value[condition_key][:, i*300:(i+1)*300]
                #    EEG_windows.append(window_data)
        
                #print(len(EEG_windows))
                
                #condition_value[condition_key] = np.array(EEG_windows)
                #print(f"The shape of the current EEG_data is: \033[1m{condition_value[condition_key].shape}\033[0m")

    return couple_dict_copy


In [ ]:
# Usa la funzione per convertire i dati e aggiungere le labels
dataset_updated_pt = prepare_data_and_labels_pt(couple_dict_data_pt)

In [ ]:
# STAMPO IL TIPO DELLA VARIABILE CHE CONTIENE OGNI DIZIONARIO PER LE COPPIE CON DENTRO I RELATIVI DIZIONARI DEI DATI E LABEL
print(f"dataset_updated_pt is: \033[1m{type(dataset_updated_pt)}\033[0m")
print()
print(f"Gli elementi della variabile dataset_updated_pt sono : \033[1m{type(dataset_updated_pt[0])}\033[0m")
print()
print(f"Esempio dell'elemento: dizionario con chiavi  \n\n {dataset_updated_pt[0]}")

In [ ]:
# STAMPO LE CHIAVI DI CIASCUN SOTTODIZIONARIO DENTRO LA LISTA DI DIZIONARI
for individual_couple, el in enumerate (dataset_updated_pt):
    for id_dict in el:
        print(el[id_dict].keys())
        print()

## STEP 4: Concatenazione dati e label per la relativa condizione sperimentale di OGNI soggetto

In questo caso, **my_subdict_list** è una **lista** in **ogni elemento** che sarà **un dizionario**, che sarà fatto di **6 chiavi**: 

- **3 chiavi** relative ai **dati di una certa condizione sperimentale**
- **3 chiavi** relative alle **labels associate ai dati di una certa condizione sperimentale**

### STEP 4.1.1: Concatenazione dati e label per la relativa condizione sperimentale di OGNI soggetto TERAPISTA

In [ ]:
# CREO LA LISTA PER CONTENERE CIASCUN SOTTODIZIONARIO

my_subdict_list_th = []

# Aggiungi tutti i sottodizionari alla lista
for id_dict in dataset_updated_th:
    first_level_dict = next(iter(id_dict))
    print(first_level_dict)
    sub_dict = id_dict[first_level_dict]
    print(sub_dict)
    print()
    my_subdict_list_th.append(sub_dict)

In [ ]:
# VEDO SHAPE E LEN DI OGNI DATO E COND EXP PER OGNI SOTTODIZIONARIO
for idx, diz in enumerate(my_subdict_list_th):

    if isinstance(diz, dict):
        print(f"\nElement at \033[1mindex {idx}\033[0m is a dictionary \n")
        
        for key, value in diz.items():
            if isinstance(value, np.ndarray):
                print(f"the \033[1marray\033[0m key {key} has a shape of {value.shape}")
            elif isinstance(value, list):
                print(f"the label key {key} has a len of {len(value)}")
    else:
        print(f"Element at index {idx} not a dictionary.")

In [ ]:
# Itera attraverso ogni dizionario nella lista
for dizionario in my_subdict_list_th:
    # Itera attraverso ogni chiave e valore nel dizionario
    for chiave, valore in dizionario.items():
        #print(dizionario.keys())
        
        # Verifica se il valore è un array numpy
        if isinstance(valore, np.ndarray):
            # Ottieni il numero di dimensioni del valore
            num_dimensioni = valore.ndim
            print(f"Chiave: \033[1m{chiave}\033[0m, Numero di dimensioni: \033[1m{num_dimensioni}\033[0m")

In [ ]:
import copy
therapists_data = copy.deepcopy(my_subdict_list_th)

In [ ]:
#therapists_data[0].keys()

#dict_keys(['baseline_1', 'vision_resp_1', 'th_resp_1', 'shared_resp_1', 
#           'baseline_1_labels', 'vision_resp_1_labels', 'th_resp_1_labels', 'shared_resp_1_labels'])

#print(f"labels: {len(therapists_data[0]['pt_resp_1_labels'])}")
#print()
#print(f"data shape: {therapists_data[0]['pt_resp_1'].shape}")

In [ ]:
print(therapists_data[0].keys())
print()
print(len(therapists_data))

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE_1_45

In [ ]:
import pickle

# Salvare l'intero dizionario annidato con pickle
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

with open(f'{base_dir}therapists_data.pkl', 'wb') as f:
    pickle.dump(therapists_data, f) 

### STEP 4.1.2: Concatenazione dati e label per la relativa condizione sperimentale di OGNI soggetto PAZIENTE

In [ ]:
# CREO LA LISTA PER CONTENERE CIASCUN SOTTODIZIONARIO

my_subdict_list_pt = []

# Aggiungi tutti i sottodizionari alla lista
for id_dict in dataset_updated_pt:
    first_level_dict = next(iter(id_dict))
    print(first_level_dict)
    sub_dict = id_dict[first_level_dict]
    print(sub_dict
         )
    print()
    my_subdict_list_pt.append(sub_dict)

In [ ]:
# VEDO SHAPE E LEN DI OGNI DATO E COND EXP PER OGNI SOTTODIZIONARIO
for idx, diz in enumerate(my_subdict_list_pt):

    if isinstance(diz, dict):
        print(f"\nElement at \033[1mindex {idx}\033[0m is a dictionary \n")
        
        for key, value in diz.items():
            if isinstance(value, np.ndarray):
                print(f"the \033[1marray\033[0m key {key} has a shape of {value.shape}")
            elif isinstance(value, list):
                print(f"the label key {key} has a len of {len(value)}")
    else:
        print(f"Element at index {idx} not a dictionary.")

In [ ]:
# Itera attraverso ogni dizionario nella lista
for dizionario in my_subdict_list_pt:
    # Itera attraverso ogni chiave e valore nel dizionario
    for chiave, valore in dizionario.items():
        #print(dizionario.keys())
        
        # Verifica se il valore è un array numpy
        if isinstance(valore, np.ndarray):
            # Ottieni il numero di dimensioni del valore
            num_dimensioni = valore.ndim
            print(f"Chiave: \033[1m{chiave}\033[0m, Numero di dimensioni: \033[1m{num_dimensioni}\033[0m")

In [ ]:
import copy
patients_data = copy.deepcopy(my_subdict_list_pt)

In [ ]:
#print(f"labels: {len(therapists_data[0]['pt_resp_1_labels'])}")
#print()
#print(f"data shape: {therapists_data[0]['pt_resp_1'].shape}")

In [ ]:
print(patients_data[0].keys())
print()
print(len(patients_data))

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE_1_45

In [ ]:
import pickle

# Salvare l'intero dizionario annidato con pickle
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

with open(f'{base_dir}patients_data.pkl', 'wb') as f:
    pickle.dump(patients_data, f) 
    

## STEP 4.1.3 (ESEGUITO DOPO WAVELET): Standardizzo o no i dati dei canali EEG per OGNI condizione sperimentale di OGNI soggetto?

**N.B.** 

**IO**
Per vedere poi il segnale ricostruito nel tempo a partire dall'analisi wavelet, conviene tenere i dati non standardizzati in modo che abbiamo il range di partenza?

**CHATGPT**
Sì, tenere i dati nel loro range originale (non standardizzati) è generalmente una buona pratica quando si intende visualizzare i segnali ricostruiti nel tempo, specialmente nel contesto dei dati EEG. 
Questo perché la standardizzazione può alterare la scala e l'intervallo dei dati, rendendo più difficile interpretare i risultati in termini di voltaggio reale (microvolt).


In [ ]:
#type(therapists_data) --> list
#type(my_subdict_list_th) --> list

#len(therapists_data) --> 13
#len(my_subdict_list_th) --> 13

## STEP 4.2: Calcolo il numero di segmenti EEG di dato e label totali per OGNI condizione sperimentale

### STEP 4.2.1: Calcolo il numero di segmenti EEG di dato e label totali per OGNI condizione sperimentale per i TERAPISTI

In [ ]:
#type(therapists_data[0]['pt_resp_1_labels'])
#OUTPUT: list

In [ ]:
'''CON LOGICA ASSEGNAZIONE NUOVA'''

# Inizializzazione dei conteggi per ogni condizione sperimentale
total_counts_th = {
    'baseline': 0,
    'th_resp': 0,
    'pt_resp': 0,
    'shared_resp': 0
}

# Iterazione su ogni terapeuta in therapists_data
for dictionary in therapists_data:

#for dictionary in my_subdict_list_th:
    
    for key, value in dictionary.items():
        # Verifica se il valore è un array numpy
        if isinstance(value, np.ndarray):
            if "baseline" in key:
                total_counts_th['baseline'] += value.shape[0]
            elif "th_resp" in key:
                total_counts_th['th_resp'] += value.shape[0]
            elif "pt_resp" in key:
                total_counts_th['pt_resp'] += value.shape[0] 
            elif "shared_resp" in key:
                total_counts_th['shared_resp'] += value.shape[0]

# Stampa dei conteggi totali per ogni condizione sperimentale
print("\nTotal number of trial data for each experimental condition in THERAPIST:\n")
for condition, count in total_counts_th.items():
    print(f"Experimental Condition: \033[1m{condition}\033[0m: \tCount: \033[1m{count}\033[0m")


### STEP 4.2.2: Calcolo il numero di segmenti EEG di dato e label totali per OGNI condizione sperimentale per i PAZIENTI

In [ ]:
#for idx, dizionario in enumerate(patients_data):
#    if isinstance(dizionario, dict):
#        print(f"\nChiavi del dizionario all'indice {idx}: {list(dizionario.keys())}")
#    else:
#        print(f"\nL'elemento all'indice {idx} non è un dizionario.")

In [ ]:
'''CON LOGICA ASSEGNAZIONE NUOVA'''

# Inizializzazione dei conteggi per ogni condizione sperimentale
total_counts_pt = {
    'baseline': 0,
    'th_resp': 0,
    'pt_resp': 0,
    'shared_resp': 0
}

# Iterazione su ogni terapeuta in therapists_data
for dictionary in patients_data:

#for dictionary in my_subdict_list_pt:

    for key, value in dictionary.items():
        # Verifica se il valore è un array numpy
           if isinstance(value, np.ndarray):
                if "baseline" in key:
                    total_counts_pt['baseline'] += value.shape[0]
                elif "th_resp" in key:
                    total_counts_pt['th_resp'] += value.shape[0]
                elif "pt_resp" in key:
                    total_counts_pt['pt_resp'] += value.shape[0]
                elif "shared_resp" in key:
                    total_counts_pt['shared_resp'] += value.shape[0]
        
# Stampa dei conteggi totali per ogni condizione sperimentale
print("\nTotal number of trial data for each experimental condition in PATIENT:\n")
for condition, count in total_counts_pt.items():
    print(f"Experimental Condition: \033[1m{condition}\033[0m: \tCount: \033[1m{count}\033[0m")


### STEP 4.2.3: Check delle shape dei dati e label per la relativa condizione sperimentale di OGNI COPPIA TERAPISTA-PAZIENTE

In [ ]:
'''NUOVA 16-17 OTTOBRE'''

import numpy as np

# Inizializza i dizionari
couples_with_trials_differences = {}
couples_with_same_trials = {}

# Itera attraverso le coppie di dizionari
for idx, (diz_th, diz_pt) in enumerate(zip(my_subdict_list_th, my_subdict_list_pt)):
    
    if isinstance(diz_th, dict) and isinstance(diz_pt, dict):
        
        # Inizializza un dizionario per la coppia corrente con diversi trial
        couples_with_trials_differences[idx + 1] = {}
        
        # Inizializza un dizionario per la coppia corrente con stessi trial
        couples_with_same_trials[idx + 1] = {}
        
        for key_th, value_th in diz_th.items():
            
            # Verifica se la chiave ha un equivalente in diz_pt
            if key_th in diz_pt:
                key_pt = key_th
                value_pt = diz_pt[key_pt]
                
                # Controllo se la stringa è la stessa e ha lo stesso suffisso numerico
                if key_th == key_pt:
                    condition = key_th  # Chiave iterata su entrambi i dizionari
                    
                    # Verifica se i valori associati sono array o liste e stampa la shape o lunghezza
                    if isinstance(value_th, np.ndarray) and isinstance(value_pt, np.ndarray):

                        # Calcolo della differenza dei trial
                        trial_difference = abs(value_th.shape[0] - value_pt.shape[0])
                        
                        # Verifica se le shape sono uguali
                        if value_th.shape == value_pt.shape:
                            # Aggiungi al dizionario delle condizioni con stessi trial
                            couples_with_same_trials[idx + 1][condition] = {
                                f"{condition}_Th": {
                                    "shape": value_th.shape,
                                },
                                f"{condition}_Pt": {
                                    "shape": value_pt.shape,
                                },
                            }
                            
                        # Se le shape sono diverse
                        else:
                            # Creazione del dizionario annidato per le shape diverse
                            couples_with_trials_differences[idx + 1][condition] = {
                                f"{condition}_Th": {
                                    "shape": value_th.shape,
                                },
                                f"{condition}_Pt": {
                                    "shape": value_pt.shape,
                                },
                                "difference": trial_difference
                            }
                    
                    # Puoi anche aggiungere la gestione per le liste se necessario

                else:
                    print(f"Keys '{key_th}' and '{key_pt}' do not match at index {idx}.")
    else:
        print(f"Element at index {idx} is not a dictionary in both lists.")

# Stampa i risultati per controllare la struttura
#print("Couples with trials differences:")
#print(couples_with_trials_differences)

#print("\nCouples with same trials:")
#print(couples_with_same_trials)


In [ ]:
# Stampa i risultati per controllare la struttura
print("\033[1mCouples with trials differences\033[0m:")
for idx, data in couples_with_trials_differences.items():
    print(f"Pair \033[1m{idx}\033[0m:")
    for condition, details in data.items():
        print(f"  Condition: {condition}, Data Shapes: {details}")

print("\n\033[1mCouples with same trials\033[0m:")
for idx, data in couples_with_same_trials.items():
    print(f"Pair \033[1m{idx}\033[0m:")
    for condition, details in data.items():
        print(f"  Condition: {condition}, Details: {details}")

In [ ]:
# Stampa le shape di dati dei terapeuti e dei pazienti
for idx in couples_with_same_trials:
    if idx in couples_with_trials_differences:
        print(f"\nComparing \033[1mPair {idx}\033[0m:")
        
        # Condizioni con differenze
        print("\nConditions with trial differences:")
        for condition, details in couples_with_trials_differences[idx].items():
            th_shape = details[f"{condition}_Th"]['shape']
            pt_shape = details[f"{condition}_Pt"]['shape']
            trial_difference = details["difference"]  # Estrai la differenza
            
            print(f"  Condition: {condition}, Therapist Shape: {th_shape}, Patient Shape: {pt_shape}, Trial Difference: {trial_difference}")

        # Condizioni con stessi trial
        print("\nConditions with same trials:")
        for condition, details in couples_with_same_trials[idx].items():
            th_shape = details[f"{condition}_Th"]['shape']
            pt_shape = details[f"{condition}_Pt"]['shape']
            print(f"  Condition: {condition}, Therapist Shape: {th_shape}, Patient Shape: {pt_shape}")

In [ ]:
'''
# Debug per i terapisti
print("\nTherapists Data Shapes:")
for idx, dictionary in enumerate(therapists_data):
    for key, value in dictionary.items():
        if isinstance(value, np.ndarray):
            print(f"Index {idx}, Key: {key}, Shape: {value.shape}")

# Debug per i pazienti
print("\nPatients Data Shapes:")
for idx, dictionary in enumerate(patients_data):
    for key, value in dictionary.items():
        if isinstance(value, np.ndarray):
            print(f"Index {idx}, Key: {key}, Shape: {value.shape}")
'''

# Debug per terapisti e pazienti
print("\nTherapists and Patients Data Shapes:")
for idx, (therapist_dict, patient_dict) in enumerate(zip(therapists_data, patients_data)):
    print(f"\n\033[1mIndex {idx}\033[0m:")
    
    # Debug per i terapisti
    print("Therapist Data:")
    for key, value in therapist_dict.items():
        if isinstance(value, np.ndarray):
            print(f"  Key: {key}, Shape: {value.shape}")
    
    # Debug per i pazienti
    print("Patient Data:")
    for key, value in patient_dict.items():
        if isinstance(value, np.ndarray):
            print(f"  Key: {key}, Shape: {value.shape}")


In [ ]:
# Sappiamo che 'my_subdict_list_th' contenga i dati dei terapeuti
# Sappiamo che 'my_subdict_list_pt' contenga i dati dei pazienti

# Controllo delle shape per ogni coppia di dati
for idx, (therapist_dict, patient_dict) in enumerate(zip(my_subdict_list_th, my_subdict_list_pt)):
    if isinstance(therapist_dict, dict):
        print(f"\nElement at \033[1mindex {idx}\033[0m in THERAPIST is a dictionary\n")
        
        for key, therapist_value in therapist_dict.items():
            if isinstance(therapist_value, np.ndarray):
                
                # Costruisce la chiave corrispondente per il paziente
                patient_key = key  # Non è necessario sostituire _1 o _2, dato che usiamo gli indici
                if patient_key in patient_dict:
                    patient_value = patient_dict[patient_key]
                    
                    # Confronta le shape
                    if isinstance(patient_value, np.ndarray):
                        if therapist_value.shape != patient_value.shape:
                            print(f"Shape mismatch for key '{key}':")
                            print(f"\tTHERAPIST shape: {therapist_value.shape}")
                            print(f"\tPATIENT shape: {patient_value.shape}")
                        else:
                            print(f"Shapes match for key '{key}': {therapist_value.shape}")
                    else:
                        print(f"Key '{patient_key}' is not an array in PATIENT data.")
                    print()
            elif isinstance(therapist_value, list):
                print(f"Label key '{key}' has a len of {len(therapist_value)}")
    else:
        print(f"Element at index {idx} in THERAPIST is not a dictionary.")

# Non è necessario eseguire un ciclo separato per i pazienti, 
# dato che il confronto avviene già nei dati del terapeuta.


## STEP 4.3 Wavelet Analysis: Teoria

### **Introduzione alla Trasformata Wavelet Discreta (DWT)**

La DWT è una tecnica di trasformata che **analizza i segnali (come i dati EEG) in diverse scale o livelli di risoluzione**. A differenza della trasformata di Fourier, che rappresenta il segnale in termini di frequenze pure, la DWT rappresenta il segnale in termini di componenti di frequenza che variano nel tempo.

**Processo di Decomposizione**
La DWT decompone un segnale in due tipi di coefficienti:

1) **Coefficienti di Approssimazione (A)**: Questi rappresentano la parte del segnale che corrisponde alle basse frequenze. Catturano la struttura generale del segnale, ovvero le informazioni di lungo termine.

3) **Coefficienti di Dettaglio (D)**: Questi rappresentano la parte del segnale che corrisponde alle alte frequenze. Catturano le variazioni rapide nel segnale, ovvero le informazioni di breve termine o i dettagli.

**Livelli di Decomposizione**
Il processo di decomposizione può essere iterato più volte. Ad ogni iterazione (o livello), il segnale viene decomposto ulteriormente:

- **Livello 1**: Decomposizione iniziale del segnale. Produce i coefficienti di dettaglio 𝐷1 e i coefficienti di approssimazione 𝐴1

- **Livello 2**: Si applica la decomposizione wavelet ai coefficienti di approssimazione 𝐴1 del livello 1. Produce i coefficienti di dettaglio 𝐷2 e i nuovi coefficienti di approssimazione 𝐴2

- **Livello 3**: Si applica la decomposizione wavelet ai coefficienti di approssimazione 𝐴2 del livello 2, e così via.
  
Questo processo continua fino al livello desiderato, producendo un insieme di coefficienti di dettaglio e uno di approssimazione per ogni livello.

<br>

**Esempio Pratico**
Immagina di avere un segnale EEG e di applicare la DWT con una wavelet db4 fino al 3° livello di decomposizione. Otterrai:

**Livello 1**:
Coefficienti di Dettaglio D1: Informazioni ad alta frequenza.
Coefficienti di Approssimazione A1: Informazioni a bassa frequenza, da decomporre ulteriormente.

**Livello 2**:
Coefficienti di Dettaglio D2: Informazioni ad alta frequenza (ma un po' più basse di D1).
Coefficienti di Approssimazione A2: Informazioni a bassa frequenza, da decomporre ulteriormente.

**Livello 3**:
Coefficienti di Dettaglio D3: Informazioni ad alta frequenza (ma un po' più basse di D2).
Coefficienti di Approssimazione A3: Informazioni a bassa frequenza che rappresentano la struttura più generale del segnale.


### Contesto dell'Analisi

- **Obiettivo**: L'analisi riguarda l'estrazione dei potenziali correlati agli eventi (ERP) dai dati EEG utilizzando la trasformata wavelet discreta (DWT).

- **Dati**: EEG pre-processato, filtrato e segmentato in epoche di 1.2 s, corretto rispetto alla baseline e rimosso degli artefatti
 
**Pre-Processing dell'EEG**:

1) **Filtraggio dei dati da 1 a 20 Hz**
2)  **Rimozione degli artefatti oculari con ICA**
3)  **Segmentazione in epoche di 1.2 s**
4)  **Correzione rispetto alla baseline (i.e., baseline correction)**
5)  **Rimozione automatica degli artefatti residui**

- **Wavelet Utilizzata: Daubechies 4 (db4)**.

Livelli di Decomposizione: Fino a 6 livelli di decomposizione con bande di frequenza specifiche per ogni livello di dettaglio e approssimazione

**Analisi con DWT**:

- Decomposizione dei segnali EEG con DWT utilizzando la wavelet db4
- Generazione di coefficienti di dettaglio (D) e di approssimazione (A) per vari livelli
- Ricostruzione dei segnali a partire dai coefficienti

<br>

### Libreria Python: PyWavelets

**PyWavelets (pywt)** è una libreria open-source per le trasformate wavelet in Python. La documentazione completa è disponibile sul loro sito web.

https://pywavelets.readthedocs.io/en/latest/

**PyWavelets (pywt) Functions**

- **pywavelets.wavedec**: https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html

- **pywt.appcoef(coeffs, wavelet, level)**: Restituisce i coefficienti di approssimazione all'ultimo livello di decomposizione specificato.
- **pywt.detcoef(coeffs, level)**: Restituisce i coefficienti di dettaglio all'ultimo livello di decomposizione specificato.


**Matlab Wavelet Toolbox**:

- **wavedec**: 
  [https://it.mathworks.com/help/wavelet/ref/wavedec.html]
  
- **appcoef**: Restituisce i coefficienti di approssimazione utilizzando la decomposizione wavelet
  [https://it.mathworks.com/help/wavelet/ref/appcoef.html]

- **detcoef**: Restituisce i coefficienti di dettaglio utilizzando la decomposizione wavelet
  [https://it.mathworks.com/help/wavelet/ref/detcoef.html]

La documentazione ufficiale di Matlab per Wavelet Toolbox può essere trovata nella Matlab Documentation.


**Altri link utili** 

[https://it.mathworks.com/matlabcentral/answers/108034-wavelet-decomposition-and-power-spectrum-of-an-eeg-signal]

link --> https://www.researchgate.net/post/How-to-perform-discrete-wavelet-transform-on-eeg-data

### **Funzioni Matlab**

#### **DiscreteWavelet.m**: funzione generica che calcola la wavelet a partire da un dato EEG organizzato in samp x ch x trials

https://it.mathworks.com/help/wavelet/ref/wavedec.html

#### **Script_Wavedec.m**: script che cicla sulle nostre varie coppie e finestre e calcola la wavelet sui nostri dati

#### **Script_PlotWaveletDiscrete_THERAPIST**: script con i plot (eventualmente da ottimizzare)

## STEP 4.3.1 Wavelet Analysis: Check livelli decomposizione

In [ ]:
# Multilevel decomposition using wavedec
# https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html

#Partial Discrete Wavelet Transform data decomposition downcoef
#https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html

#Maximum decomposition level 

# 1) dwt_max_level 
# 2) dwtn_max_level

# 1) dwt_max_level 
#pywt.dwt_max_level(data_len, filter_len)

#Compute the maximum useful level of decomposition.

# 2) dwtn_max_level
#pywt.dwtn_max_level(shape, wavelet, axes=None)

#Compute the maximum level of decomposition for n-dimensional data.
#This returns the maximum number of levels of decomposition suitable 
#for use with wavedec, wavedec2 or wavedecn.

import pywt
max_decomposition_level = pywt.dwtn_max_level((300,), 'db4')
print(f"\033[1mMaximum Decomposition Level\033[0m for EEG trial data is: \033[1m{max_decomposition_level}\033[0m")
print(f"\n\033[1mMaximum Decomposition Level\033[0m is a : {type(max_decomposition_level)}")

## STEP 4.3.2 Wavelet Analysis: Functions 'wavedec' & 'waverec' implementation
### Visualization of Single Subject Data for which Wavelet is performed

## STEP 4.3.2.1 Wavelet Analysis: Pywavelets.Wavedec function & Pywavelets.Waverec function

#### **Decomposizione del segnale in livelli ed estrazione dei Coefficienti**

Quando si lavora con la **trasformata wavelet discreta (DWT)** utilizzando pywt.wavedec, 
è importante capire come sono organizzati e come vengono utilizzati per la ricostruzione

1) i coefficienti di approssimazione 
2) i coefficienti di dettaglio

- **Coefficiente di Approssimazione dell'Ultimo Livello (cA_n)**:
    Questo coefficiente (coeffs[0] nella lista coeffs restituita da pywt.wavedec) 
    rappresenta l'approssimazione all'ultimo livello della decomposizione.
    È il risultato dell'applicazione della trasformata wavelet all'ultimo livello (level)
    del segnale originale.
    
- **Coefficiente di Dettaglio dell'Ultimo Livello (cD_n)**:
    Questo coefficiente (coeffs[1] fino a coeffs[level] nella lista coeffs 
    restituita da pywt.wavedec) rappresenta i dettagli all'ultimo livello della decomposizione.
    Ogni coeffs[l] (dove l va da 1 a level) è il risultato della trasformata wavelet 
    applicata al segnale originale a quel livello specifico.

<br>

#### **Ricostruzione dei Coefficienti dal dominio wavelet al dominio del tempo**

- **Per i coefficienti di approssimazione all'ultimo livello (cA_n)**:
  Questi sono usati direttamente per la ricostruzione dell'approssimazione 
  dell'ultimo livello del segnale originale. 
  Questo è perché cA_n rappresenta già l'approssimazione al livello n della decomposizione.

- **Per i coefficienti di dettaglio (che sono cD_n, cD_{n-1}, ..., cD_1)**:
  Questi sono utilizzati nella ricostruzione del dettaglio del segnale originale.
  Nella ricostruzione, cD_n rappresenta i dettagli all'ultimo livello, cD_{n-1} rappresenta i dettagli al penultimo
  livello e così via fino a cD_1 che rappresenta i dettagli al primo livello.

  (Non chiaro: La somma ponderata di questi dettagli ricostruiti insieme all'approssimazione dell'ultimo livello fornisce la
  ricostruzione del segnale originale...?)

#### Perché questa distinzione?

I **coefficienti di approssimazione dell'ultimo livello (cA_n)** sono **SUFFICIENTI**
per rappresentare l'approssimazione finale del segnale decomposto fino a quel livello.

I **coefficienti di dettaglio** sono utilizzati **in combinazione** per ricostruire il dettaglio del segnale originale a partire **dall'ULTIMO livello fino al PRIMO livello di decomposizione**.

Questa distinzione è **CRUCIALE**, perché 

- il **livello più alto di approssimazione (cA_n)** è **direttamente** utilizzato per rappresentare l'approssimazione finale, 

- mentre **i dettagli (da cD_n a cD_1)** sono utilizzati **per ricostruire i dettagli del segnale originale a diversi livelli di risoluzione**

Spero che questa spiegazione chiarisca il motivo nella ricostruzione dei segnali utilizzando la DWT si usa 

- coeffs[0] per cA = (i.e., cA5)
- coeffs[1:] per cD = (i.e., cD5, cD4, cD3, cD2, cD1)

<br>
<br>

#### **IN SINTESI**:


**Struttura dell'OUTPUT di "coeffs" (variabile che prende in input pywt.wavedec)**

    ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ----
     
    Se eseguo una decomposizione a più livelli, coeffs è una lista di array ordinata come segue:
    
    coeffs[0]: Coefficienti di approssimazione del livello più alto di decomposizione (livello n se hai n livelli).
    
    coeffs[1]: Coefficienti di dettaglio del livello n.
    
    coeffs[2]: Coefficienti di dettaglio del livello n-1.
    
    ...
    
    coeffs[n]: Coefficienti di dettaglio del livello 1 (livello più basso).
    ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ----
    

L'output di "**coeffs**" da 

- come **primo elemento** (i.e. coeffs[0]) i **coefficienti di approssimazione per solo l'ULTIMO livello di decomposizione**... e **SOLO quelli dell'ULTIMO livello**, vengono usati **per ricostruire le componenti di APPROSSIMAZIONE del segnale ORIGINALE fino a quel livello di decomposizione**  

...  

- mentre **tutti gli altri elementi di "coeffs"** (i.e. coeffs[1:]) sono i **coefficienti di dettaglio di TUTTI i livelli di livelli di decomposizione (dall'ULTIMO a tutti i PRECEDENTI) del segnale ORIGINALE**...e **TUTTI** quanti vengono combinati (tramite una somma ponderata) **per ricostruire le componenti di DETTAGLIO del segnale ORIGINALE fino a quel livello di decomposizione considerato**

<br>
<br>
<br>

#### **SPIEGAZIONE CODICE PARTE 1 (ESTRAZIONE COEFFICIENTI)**: pywt.wavedec


Leggendo sulla documentazione, dalla **funzione** ***pywt.wavedec*** https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html, 


 ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ 
    ESTRAZIONE DEI COEFFICIENTI DI APPROSSIMAZIONE E DETTAGLIO PER IL LIVELLO DI DECOMPOSIZIONE CONSIDERATO
    
    Multilevel decomposition using wavedec (Multilevel 1D Discrete Wavelet Transform of data)
    https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html
    
    pywt.wavedec(data, wavelet, mode='symmetric', level=None, axis=-1)
    
    Parameters:
        
        data: array_like
            Input data
        
        wavelet: Wavelet object or name string
            Wavelet to use
        
        mode: str, optional
            Signal extension mode, see Modes.
        
        level: int, optional
        Decomposition level (must be >= 0). If level is None (default) then it will be calculated using the dwt_max_level 
        function.
        
        axis: int, optional
            Axis over which to compute the DWT. If not given, the last axis is used.
            
    Returns: 
        [cA_n, cD_n, cD_n-1, …, cD2, cD1] : list
    
        Ordered list of coefficients arrays where n denotes the level of decomposition. 
    
        The first element (cA_n) of the result is approximation coefficients array and
        the following elements (cD_n - cD_1) are details coefficients arrays.          
------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ 

    

La funzione ti da ***in output*** **UNA lista**, che ha

1) come ***primo elemento*** i coefficienti di approssimazione per solo l'ULTIMO livello di decomposizione

2) mentre invece ***tutti gli altri elementi***  di questa lista sono i coefficienti di dettaglio di TUTTI i livelli di livelli di decomposizione (dall'ULTIMO a tutti i PRECEDENTI) del segnale ORIGINALE

E insieme, 1) e 2) , da quel che ho capito, servono per ricostruire poi il segnale originale a diverse scale...

Ma l'output di ***pywt.wavedec***  è solo UNA lista di array, che fa riferimento ai ***coeff di approx e dettaglio*** rispetto a ***SOLO l'ULTIMO livello di decomposizione del segnale originale*** (campionato a 250Hz).

Quindi tipo sarà: 

[ **1° elemento**: [np.array *coeff approx* ultimo livello decomp], **2° elemento**: [np.array *coeff dettaglio* ultimo livello decomposizione] **3° elemento**:  [np.array *coeff dettaglio* penultimo livello decomposizione] etc...] ... ]


Quindi, bisogna crearsi la variabile ***'C'*** che dovrebbe contenere, 

per **ogni trial**, di **ogni canale**,  i ***coeff di approx e dettaglio*** rispetto alla **specifica condizione sperimentale** (che vengono inseriti dentro la variabile **'coeff'** su cui si applica la funzione ***pywt.wavedec*** https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html...)

<br>
<br>
<br>

#### **SPIEGAZIONE CODICE PARTE 2 (RICOSTRUZIONE SEGNALI A PARTIRE DAI COEFFICIENTI ESTRATTI)**: pywt.waverec

Ora, se tutto quello che ho detto sopra è vero...

Allora siccome uso ***pywt.waverec*** (che fa la Multilevel 1D Inverse Discrete Wavelet Transform, https://pywavelets.readthedocs.io/en/latest/ref/idwt-inverse-discrete-wavelet-transform.html#pywt.waverec)

 ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ 
    *RICOSTRUZIONE DEL SEGNALE MEDIO A PARTIRE DAI COEFF MEDI DI APPROX e DETTAGLIO RELATIVI A QUEL LIVELLO DI DECOMPOSIZIONE CONSIDERATO*
    
    Dettagli della Ricostruzione
    La ricostruzione è eseguita come segue:
    
    Per i Dettagli (D):
    
    Utilizzi pywt.waverec con i coefficienti di dettaglio per un livello specifico e 
    i coefficienti di approssimazione per i livelli superiori.
    
    D[tr, ch, :, l - 1] ricostruisce il segnale utilizzando SOLO 
    i coefficienti di dettaglio per il livello l-1 e 
    azzerando gli altri coefficienti.
    
    Per le Approssimazioni (A):
    
    Utilizzi pywt.waverec con solo i coefficienti di approssimazione dell'ultimo livello 
    per ottenere la ricostruzione dell'approssimazione.
    
    A[tr, ch, :, l - 1] ricostruisce il segnale utilizzando SOLO 
    i coefficienti di approssimazione per il livello l e
    azzerando i coefficienti di dettaglio.


    pywt.waverec: https://pywavelets.readthedocs.io/en/latest/ref/idwt-inverse-discrete-wavelet-transform.html

    pywt.waverec (coeffs, wavelet, mode='symmetric', axis=-1)
    Multilevel 1D Inverse Discrete Wavelet Transform.
    
    Parameters:
    coeffs: array_like
        Coefficients list [cAn, cDn, cDn-1, …, cD2, cD1]
    
    wavelet: Wavelet object or name string
        Wavelet to use
    
    mode: str, optional
        Signal extension mode, see Modes.

    *******
    axis: int, optional
    Axis over which to compute the inverse DWT. If not given, the last axis is used.
    *******

    Notes

    It may sometimes be desired to run waverec with some sets of coefficients omitted. 
    This can best be done by setting the corresponding arrays to zero arrays of matching shape and dtype. 
    Explicitly removing list entries or setting them to None is not supported.

    Specifically, to ignore detail coefficients at level 2, one could do:
    
    coeffs[-2] = np.zeros_like(coeffs[-2])
 ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ ------ 

<br>

Sulle variabili ***"A"*** e ***"D"*** che contengono i ***coeff di approx*** e ***dettaglio***, 

su **ogni trial**, di **ogni canale**, rispetto ad **ogni condizione sperimentale**...

Alla fine, ottengo la ***media dei coefficienti di approx e  dettaglio*** associati ad **ogni trial**, su **ogni canale**, di **ogni condizione sperimentale**...

Ed è da queste variabili qui che son ***"Dm"***  ed ***"Am"***, che io posso plottarmi la forma d'onda dei segnali ricostruiti!


<br>

Per **ogni trial** di **ogni canale**, riferito ad una **stessa condizione sperimentale** avrò una variabile "**coeffs**", che contiene 

1) i coefficienti di approssimazione (primo elemento di "coeffs") e
2) i relativi coefficienti di dettaglio (tutti gli altri elementi dentro "coeffs") 

associati ad un certo livello di decomposizione

Ossia, siccome ho 5 massimi livelli di decomposizione, per ogni trial avrò 5 liste associate a quel trial di quello specifico canale?


<br>
<br>

**Esempio con 5 Livelli di Decomposizione**

Impostando impostato un massimo di 5 livelli di decomposizione, allora per ogni trial e canale dovrei avere:

**Al 1° Livello**:

-1 array per i coefficienti di approssimazione del livello 1 (il livello più alto in quel momento)^
-1 array per i coefficienti di dettaglio al livello 1 (il livello più basso in quel momento)^

**coeffs = [cA1, cD1]**

<br>

**Al 2° Livello**:

-1 array per i coefficienti di approssimazione del livello 2 (il livello più alto in quel momento)^
-2 array per 
    i coefficienti di dettaglio al livello 2 (il livelli più alto in quel momento) e 
    i coefficienti di dettaglio al livello 1 (il livello più basso in quel momento)^

**coeffs = [cA2, cD2, cD1]**

<br>

**Al 3° Livello**:

-1 array per i coefficienti di approssimazione del livello 3 (il livello più alto in quel momento)^
-3 array per 
    i coefficienti di dettaglio al livello 3 (il livello più alto in quel momento) 
    i coefficienti di dettaglio al livello 2 (il penultimo livello più alto in quel momento)
    i coefficienti di dettaglio al livello 1 (il livello più basso in quel momento)^

**coeffs = [cA3, cD3, cD2, cD1]**

<br>

**Al 4° Livello**:

-1 array per i coefficienti di approssimazione del livello 4 (il livello più alto in quel momento)^
-4 array per 
    i coefficienti di dettaglio al livello 4 (il livello più alto in quel momento) 
    i coefficienti di dettaglio al livello 3 (il penultimo livello più alto in quel momento) 
    i coefficienti di dettaglio al livello 2 (il terzultimo livello più alto in quel momento)
    i coefficienti di dettaglio al livello 1 (il livello più basso in quel momento)^

**coeffs = [cA4 cD4, cD3, cD2, cD1]**

<br>

**Al 5° Livello**:

-1 array per i coefficienti di approssimazione del livello 5 (il livello più alto in quel momento)^
-4 array per 
    i coefficienti di dettaglio al livello 5 (il livello più alto in quel momento) 
    i coefficienti di dettaglio al livello 4 (il penultimo livello più alto in quel momento) 
    i coefficienti di dettaglio al livello 3 (il terzultimo livello più alto in quel momento)
    i coefficienti di dettaglio al livello 2 (il quartultimo livello più basso in quel momento)^
    i coefficienti di dettaglio al livello 1 (il livello più basso in quel momento)^


Quindi, coeffs per un dato trial e canale avrà la seguente struttura (se fossimo al 5° livello di decomposizione!):

**coeffs = [cA5, cD5, cD4, cD3, cD2, cD1]**

<br>
<br>

N.B.

Qui il "**il livello più alto**" è quello **più profondo**, mentre "**i livelli più bassi**" si riferiscono ai livelli primari di
decomposizione, ossia **quelli più vicini alla ricostruzione ORIGINALE del segnale**!



## STEP 4.3.2.1 Wavelet Analysis: Example Single Therapist

#### **One experimental condition** for all levels of decompositions

In [ ]:
''' LAST UPDATE - PROVA 31/07/2024  C ed L matrici BIDIMENSIONALI

C ed L hanno 2 dimensioni, 
ossia si presentano come una matrice bidimensionale, che rappresenta i coefficienti di approssimazione e di dettaglio, per ogni livello

'''
import numpy as np
import pywt

max_decomposition_level = pywt.dwtn_max_level((300,), 'db4')
level = max_decomposition_level  # Livello di decomposizione della wavelet
wavelet = 'db4'  # Tipo di wavelet da utilizzare

def compute_coefficients_per_level(signal, wavelet, max_level):
    
    '''Calcola i coefficienti di approssimazione e dettaglio per ogni livello di decomposizione'''
    all_coeffs = []

    for l in range(1, max_level + 1):

        #https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html
        coeffs = pywt.wavedec(signal, wavelet, level=l)
        all_coeffs.append(coeffs)
    
    return all_coeffs

    
    
def discrete_wavelet(EEG_data, level, wavelet):
    
    '''Cicla su tutti tutti i trial (di ogni condizione sperimentale) di ogni canale ed esegue la DWT analysis'''
    
    num_trials, num_channels, num_samples = EEG_data.shape
    
    lev_check = int(np.floor(np.log2(num_samples)))
    if level > lev_check:
        level = lev_check

    '''
    Per mantenere un'organizzazione chiara e strutturata dei coefficienti di approssimazione e dettaglio per ogni livello, trial e canale, 
    il modo migliore per farlo è utilizzare array numpy con dtype=object per preservare la struttura gerarchica e le dimensioni variabili dei coefficienti.
    In questo modo, sarà più facile accedere e analizzare i coefficienti per ogni livello di decomposizione.
    
    '''
    # C e L sono array numpy con dtype=object per contenere i coefficienti
    C = np.empty((num_trials, num_channels), dtype=object)
    L = np.empty((num_trials, num_channels), dtype=object)
    
    #C = []
    #L = []
    
    cA = [[] for _ in range(level)]
    cD = [[] for _ in range(level)]
    
    D = np.zeros((num_trials, num_channels, num_samples, level))
    A = np.zeros((num_trials, num_channels, num_samples, level))

    #print(f"\t\t\033[1mSI OTTENGONO COEFF APPROX e DETAIL SOLO PER ULTIMA COND SPERIMENTALE ('SHARED_RESP') DEL 1° SOGGETTO!\033[0m\n")

    for tr in range(num_trials):
        for ch in range(num_channels):

            # "all_coeffs", (output di "coeffs_all_levels") ritornato dalla funzione "compute_coefficients_per_level" appenderà poi 
            
            # i coeff di approx e dettaglio del livello specificato alla fine dentro "trial_C", 
            # mentre dentro "trial_L" la sua lunghezza di coefficienti associati 

            coeffs_all_levels = compute_coefficients_per_level(EEG_data[tr, ch, :], wavelet, level)
            
            trial_C = []
            trial_L = []

            #Successivamente, per ogni livello l:
                        
            for l, coeffs in enumerate(coeffs_all_levels):
                
                #trial_C.append(coeffs) aggiunge i coefficienti calcolati per il livello corrente a trial_C.
                #trial_L.append([len(c) for c in coeffs]) aggiunge la lunghezza dei coefficienti per il livello corrente a trial_L.
                
                trial_C.append(coeffs)
                trial_L.append([len(c) for c in coeffs])
                
                #cA[l].append(coeffs[0]) aggiunge i coefficienti di approssimazione del livello corrente a cA.
                #cD[l].append(coeffs[1:]) aggiunge i coefficienti di dettaglio del livello corrente a cD.
                
                cA[l].append(coeffs[0])
                cD[l].append(coeffs[1:])

                #https://pywavelets.readthedocs.io/en/latest/ref/idwt-inverse-discrete-wavelet-transform.html

                'OLD VERSIONS'
                #D[tr, ch, :, l] = pywt.waverec([coeffs[i] if i == l + 1 else np.zeros_like(coeffs[i]) for i in range(len(coeffs))], wavelet)
                #A[tr, ch, :, l] = pywt.waverec([coeffs[0] if i == 0 else np.zeros_like(coeffs[i]) for i in range(len(coeffs))], wavelet)

                # Ricostruzione del segnale con solo i coefficienti di dettaglio per il livello l
                D[tr, ch, :, l] = pywt.waverec(
                    [np.zeros_like(coeffs[0]) if i == 0 else (coeffs[i] if i == l + 1 else np.zeros_like(coeffs[i]))
                     for i in range(len(coeffs))], wavelet)
                
                # Ricostruzione del segnale con solo i coefficienti di approssimazione
                A[tr, ch, :, l] = pywt.waverec(
                    [coeffs[0] if i == 0 else np.zeros_like(coeffs[i])
                     for i in range(len(coeffs))], wavelet)
            
            C[tr, ch] = trial_C
            L[tr, ch] = trial_L

            
            #C.append(trial_C)
            #L.append(trial_L)

            '''
            C = [
                # Trial 1, Channel 1
                [
                    [cA1, cD1],      # Livello 1
                    [cA2, cD2, cD1], # Livello 2
                    [cA3, cD3, cD2, cD1]  # Livello 3
                ],
                # Trial 1, Channel 2
                [
                    [cA1, cD1],
                    [cA2, cD2, cD1],
                    [cA3, cD3, cD2, cD1]
                ],
                ...
            ]
            
            L = [
                # Trial 1, Channel 1
                [
                    [len(cA1), len(cD1)],      # Livello 1
                    [len(cA2), len(cD2), len(cD1)], # Livello 2
                    [len(cA3), len(cD3), len(cD2), len(cD1)]  # Livello 3
                ],
                # Trial 1, Channel 2
                [
                    [len(cA1), len(cD1)],
                    [len(cA2), len(cD2), len(cD1)],
                    [len(cA3), len(cD3), len(cD2), len(cD1)]
                ],
                ...
            ]

            '''

    Dm = np.mean(D, axis=0)
    Am = np.mean(A, axis=0)

    wave = {
        'C': C,
        'L': L,
        #'cA': [np.array(c) for c in cA],
        #'cD': [np.array(c) for c in cD],
        'cA': cA,
        'cD': cD,
        'D': D,
        'A': A,
        'Dm': Dm,
        'Am': Am
    }

    return wave

# Itera sui dizionari nella lista
for idx, data_dict in enumerate(therapists_data):
    if idx == 0:  # Applica la wavelet solo per il primo dizionario
        print(f"\033[1mDizionario {idx + 1}\033[0m:\n")
        for key, value in data_dict.items():
            if isinstance(value, np.ndarray):  # Verifica se il valore è un np.array
                print(f"Applicazione wavelet per '\033[1m{key}\033[0m'\n")
                # Applica la wavelet
                th_1_wavelet_results_example = discrete_wavelet(value, level, wavelet)
                print()
            else:
                print(f"'\033[1m{key}\033[0m' non è un np.array, non applicare la wavelet")





## STEP 4.3.2.1 Wavelet Analysis: Example Single Therapist

#### **All experimental conditions** for all levels of decompositions


#### **All experimental conditions** for all levels of decompositions

Quando **ricostruisci il segnale dal dominio delle wavelet al dominio del tempo**, 
per un determinato livello di decomposizione, **utilizzi i coefficienti di approssimazione e dettaglio come segue**:

<br>

- **Coefficiente di Approssimazione dell'Ultimo Livello Considerato**:
  Questo è il coefficiente di approssimazione per l'ultimo livello di decomposizione
  che stai considerando. In altre parole, se stai ricostruendo il segnale al Livello 3,
  userai il coefficiente di approssimazione corrispondente al Livello 3.

- **Coefficienti di Dettaglio per i Livelli Superiore**:
  Utilizzerai i coefficienti di dettaglio per i livelli che sono superiori all'ultimo livello di decomposizione considerato.
  Ad esempio, se stai ricostruendo il segnale per il Livello 2, userai i coefficienti di dettaglio per il Livello 1 e il
  Livello 2.

<br>


- **Dettagli della Ricostruzione** Quando ricostruisci per un certo livello di decomposizione:

  - **Per il Livello 3**: Usa il coefficiente di approssimazione del Livello 3 ed Usa i coefficienti di dettaglio dei
    Livelli 1, 2 e 3.
  - **Per il Livello 2**: Usa il coefficiente di approssimazione del Livello 2 ed Usa i coefficienti di dettaglio dei
    Livelli 1 e 2.

<br>

- **Applicazione Pratica**
Am e Dm: Questi rappresentano i coefficienti medi di approssimazione e dettaglio rispettivamente,
calcolati su tutti i trial e canali per ogni condizione sperimentale.

Se **consideri un certo livello di decomposizione**, Am e Dm verranno presi dal livello di decomposizione corrispondente.

Per un livello specifico, 
- **Am** sarà il coefficiente di approssimazione dell'ultimo livello di decomposizione considerato e
- **Dm** sarà il coefficiente di dettaglio per i livelli fino a quello specificato.



In [ ]:
''' LAST UPDATE - PROVA 01/08/2024 

C ed L le trasformo in matrici a 3 dimensioni, 
ossia si presentano come una matrice tridimensionale con:

trials, canali, coeff relativi a quel livello di decomposizione

Inoltre, appendo i risultati di ogni discrete wavelet effettuata su ogni livello per ogni condizione sperimentale separatamente 
in una struttura 'wave'   
(evitando la sovrascrittura dei coefficienti di ogni livello quando si itera tra le diverse condizioni sperimentali)


Su entrambe le funzioni

pywt.wavedec(https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html) e
pywt.waverec (https://pywavelets.readthedocs.io/en/latest/ref/idwt-inverse-discrete-wavelet-transform.html)

in entrambe, c'è scritto un parametro che è 'axis'

----- ----- ----- ----- ----- ----- ----- ----- -----
----- ----- ----- ----- ----- ----- ----- ----- -----
in pywt.wavedec c'è scritto:

axis: int, optional
Axis over which to compute the DWT. If not given, the last axis is used.

e la mia shape dei dati originaria è (num_trials, n_channels, punti temporali per trial)
quindi in questo caso la funzione "pywt.wavedec" dovrebbe fare le decomposizioni sui dati di ogni trial (lungo l'asse temporale) e questo è corretto?



----- ----- ----- ----- ----- ----- ----- ----- -----
----- ----- ----- ----- ----- ----- ----- ----- -----
in pywt.waverec c'è scritto:

axis: int, optional
Axis over which to compute the inverse DWT. If not given, the last axis is used.


la mia ricostruzione viene a partire da degli array che son D ed A che son rispettivamente 
la ricostruzione a partire dal coeff di dettaglio o di approssimazione del livello considerato..

Nel mio codice D ed A vengono inizializzati con questa shape

# Prepariamo array per i coefficienti di dettaglio e approssimazione
    D = np.zeros((num_trials, num_channels, num_samples, level))
    A = np.zeros((num_trials, num_channels, num_samples, level))

quindi la ricostruzione del segnale, a partire dai relativi coefficienti, viene fatta sull'ultimo asse, che è 
il set di coefficienti presi dal livello di decomposizione considerato a quel momento 
come l'ultimo al ciclo corrente nel loop di ogni trial (dunque lungo l'asse temporale)....

anche qui allora la funzione "pywt.waveeec" dovrebbe fare la ricostruzione 
a partire dai coefficienti dell'i-esimo livello considerato... e questo è corretto? 

'''

import numpy as np
import pywt

# Calcola il livello massimo di decomposizione
max_decomposition_level = pywt.dwtn_max_level((300,), 'db4')
level = max_decomposition_level  # Livello di decomposizione della wavelet
wavelet = 'db4'  # Tipo di wavelet da utilizzare

def compute_coefficients_per_level(signal, wavelet, max_level):
    '''Calcola i coefficienti di approssimazione e dettaglio per ogni livello di decomposizione'''
    all_coeffs = []
    for l in range(1, max_level + 1):

        #https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html
        coeffs = pywt.wavedec(signal, wavelet, level=l)
        all_coeffs.append(coeffs)
    return all_coeffs


def discrete_wavelet(EEG_data, level, wavelet):
    
    '''
    Cicla su tutti i trial (di ogni condizione sperimentale) di ogni canale ed esegue la DWT analysis
    '''
    
    num_trials, num_channels, num_samples = EEG_data.shape
    lev_check = int(np.floor(np.log2(num_samples)))
    if level > lev_check:
        print(f"max level of decomposition was exceeded!")
    else:
        print(f"\033[1mMax Level of decomposition\033[0m corresponds to the one calculated, which is \033[1m{level}\033[0m\n\n")

    '''
    Per mantenere un'organizzazione chiara e strutturata dei coefficienti di approssimazione e dettaglio
    per ogni livello, trial e canale, 
    il modo migliore per farlo è utilizzare array numpy con dtype = object 
    per preservare la struttura gerarchica e le dimensioni variabili dei coefficienti.
    
    In questo modo, sarà più facile accedere e analizzare i coefficienti per ogni livello di decomposizione.
    '''

    # Dimensioni per C e L
    C = np.empty((num_trials, num_channels, level), dtype=object)
    L = np.empty((num_trials, num_channels, level), dtype=object)

    # Prepariamo array per i coefficienti di dettaglio e approssimazione
    D = np.zeros((num_trials, num_channels, num_samples, level))
    A = np.zeros((num_trials, num_channels, num_samples, level))

    #Per ogni trial...
    for tr in range(num_trials):

        #Per ogni canale...
        for ch in range(num_channels):

            #Mi calcolo i coefficienti di detail e approx per ogni livello di ogni trial di ogni canale
            coeffs_all_levels = compute_coefficients_per_level(EEG_data[tr, ch, :], wavelet, level)

            trial_C = []
            trial_L = []

            for l, coeffs in enumerate(coeffs_all_levels):
                trial_C.append(coeffs)
                trial_L.append([len(c) for c in coeffs])

                '''
                Ricostruzione dei segnali:
                
                - Ricostruzione con solo i coefficienti di dettaglio (D)
                
                Per ogni livello l, la variabile D è costruita utilizzando solo i coefficienti di dettaglio 
                per quel livello specifico. 
                Nella ricostruzione, i coefficienti di dettaglio per i livelli superiori vengono utilizzati, 
                mentre i coefficienti di dettaglio per i livelli inferiori vengono impostati a zero.
                
                Livello 1: Solo cD1 è utilizzato. D sarà la ricostruzione a partire da cD1, e cA1 è ignorato.
                Livello 2: Solo cD2 e cD1 sono utilizzati. D sarà la ricostruzione a partire da cD2 e cD1, mentre cA2 e cA1 sono ignorati.
                Livello 3 e oltre: Saranno inclusi cD3, cD2, cD1 e così via, con i coefficienti di dettaglio per i livelli superiori e 
                tutti i coefficienti di approssimazione saranno impostati a zero.

                Quindi significa che, per il livello l, si usano solo i coefficienti di dettaglio fino al livello l, 
                e gli altri coefficienti sono impostati a zero.
                '''
                
                # Ricostruzione del segnale con solo i coefficienti di dettaglio per il livello l
                D[tr, ch, :, l] = pywt.waverec(
                    [np.zeros_like(coeffs[0]) if i == 0 else (coeffs[i] if i == l + 1 else np.zeros_like(coeffs[i]))
                     for i in range(len(coeffs))], wavelet)

                '''
                Ricostruzione dei segnali:
                
                - Ricostruzione con solo i coefficienti di approssimazione (A)
                
                Per ogni livello l, la variabile A è costruita utilizzando solo il coefficiente di approssimazione per quel livello specifico. 
                I coefficienti di dettaglio vengono ignorati.

                Livello 1: Solo cA1 è utilizzato. A sarà la ricostruzione a partire da cA1.
                Livello 2: Solo cA2 è utilizzato, mentre cD2 e cD1 sono ignorati.
                Livello 3 e oltre: Solo cA3, cA2, e così via, e i coefficienti di dettaglio sono ignorati.

                Quindi significa che, per il livello l, si usano solo i coefficienti di approssimazione fino al livello l, 
                e i coefficienti di dettaglio vengono ignorati.

                '''
                
                # Ricostruzione del segnale con solo i coefficienti di approssimazione

                # https://pywavelets.readthedocs.io/en/latest/ref/idwt-inverse-discrete-wavelet-transform.html
                
                A[tr, ch, :, l] = pywt.waverec(
                    [coeffs[0] if i == 0 else np.zeros_like(coeffs[i])
                     for i in range(len(coeffs))], wavelet)

            C[tr, ch] = trial_C
            L[tr, ch] = trial_L

    print(f"D shape before mean: {D.shape}")
    print(f"A shape before mean: {A.shape}")

    Dm = np.mean(D, axis = 0)
    Am = np.mean(A, axis = 0)

    print(f"Dm shape after mean: {Dm.shape}")
    print(f"Am shape after mean: {Am.shape}")

    wave = {
        'C': C,
        'L': L,
        'D': D,
        'A': A,
        'Dm': Dm,
        'Am': Am
    }

    return wave

# Itera sui dizionari nella lista e calcola la wavelet per ogni condizione sperimentale
th_1_wavelet_results_per_condition = {}


# Itera sui dizionari nella lista
for idx, data_dict in enumerate(therapists_data):
    if idx == 0:  # Applica la wavelet solo per il primo dizionario
        print(f"\033[1mDizionario {idx + 1}\033[0m:\n")
        for key, value in data_dict.items():
            if isinstance(value, np.ndarray):  # Verifica se il valore è un np.array
                print(f"Applicazione wavelet per '\033[1m{key}\033[0m'\n")
                
                # Applica la wavelet
                wavelet_results = discrete_wavelet(value, level, wavelet)
                print()
                # Salva i risultati nella struttura wavelet_results_per_condition
                th_1_wavelet_results_per_condition[key] = wavelet_results
            else:
                print(f"'\033[1m{key}\033[0m' non è un np.array, non applicare la wavelet")


In [ ]:
# Esempio di accesso ai risultati
for condition, results in th_1_wavelet_results_per_condition.items():
    
    # Stampa le dimensioni di C e L per ogni condizione sperimentale
    print(f"Shape di C per la condizione '{condition}': {results['C'].shape}")
    print(f"Shape di L per la condizione '{condition}': {results['L'].shape}")
    print()

    # Verifica del contenuto delle strutture dati
    num_levels = results['C'].shape[2]  # Ottieni il numero di livelli
    for level_idx in range(num_levels):
        print(f"\n\033[1mContenuto di C\033[0m per la condizione '\033[1m{condition}\033[0m', primo trial, primo canale, \033[1mlivello {level_idx + 1}\033[0m:")
        print(results['C'][0, 0, level_idx])
        print(f"\n\033[1mContenuto di L\033[0m per la condizione '\033[1m{condition}\033[0m', primo trial, primo canale,\033[1mlivello {level_idx + 1}\033[0m:")
        print(results['L'][0, 0, level_idx])
        print()

## STEP 4.3.2.1.1 Plot Example - Single Therapist


#### **ISTRUZIONI PLOT**

1) Il nome dell'**asse y** è 'voltaggio in μV" e il nome dell'**asse x** è 'tempo' in cui viene inserito un conteggio del tempo in termini di millisecondi (sapendo che la finestra è di **1.2 secondi totale**, con 200 mms di pre-stimolo)

2) In corrispondenza dei **200 mms**, inserisco una **barra verticale nera tratteggiata**, che indica il momento in cui gli stimoli della frame della finestra di 'Responsibility' vengono presentati (i.e., appellativo nominale e consapevolezza di chi ha scelto la carta non corretta) ...

3) La legenda indica i colori delle forme d'onda associate alle diverse condizioni sperimentali; è stato inserita fuori dall'immagine (in modo da non ostruire col plot delle diverse forme d'onda); in caso, aumentare la grandezza del font se fosse troppo piccolo

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

# Indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali: Fz, Cz, Pz

# Nomi dei canali
nomi_canali = ['Fz', 'Cz', 'Pz']

# Livelli di decomposizione desiderati (livelli 3, 4, 5 corrispondenti agli indici 2, 3, 4 in Python)
livelli_di_decomposizione = [2, 3, 4]

# Colori per le condizioni sperimentali
colori_condizioni = {
    'baseline': 'green',
    'th_resp': 'blue',
    'vision_resp': 'purple',
    'shared_resp': 'red'
}

# Frequenza di campionamento
frequenza_campionamento = 250  # Hz
campioni_totali = 300  # Numero di campioni
durata_finestra = 1.2  # Secondi
pre_stimolo_ms = 200  # Millisecondi

# Creazione della figura con una griglia 3x3 (3 canali x 3 livelli di decomposizione)
fig, axs = plt.subplots(3, 3, figsize = (20, 25), sharex=True, sharey=True)  # Aumenta la larghezza a 20
fig.suptitle('\n\nRicostruzione del Segnale mediato dai Coefficienti di Approssimazione per ogni Condizione Sperimentale e Livello di Decomposizione di interesse - Terapista 1', fontsize=16)

# Creazione dell'asse x in millisecondi
asse_x_ms = np.linspace(-pre_stimolo_ms, durata_finestra * 1000 - pre_stimolo_ms, campioni_totali)

# Itera su ogni condizione sperimentale e livello di decomposizione
for idx, (condizione, risultati) in enumerate(th_1_wavelet_results_per_condition.items()):
    
    # Determina il colore basato sulla condizione sperimentale
    colore = 'black'  # Colore di default
    
    for keyword, c in colori_condizioni.items():
        if keyword in condizione:
            colore = c
            break
                                           #La Shape di risultati['Am'] per tutti i canali EEG: 
                                           #(num_canali, num_samples, num_livelli)

                                           #dove, "num_livelli" = n° coeff del relativo livello di ricostruzione 
                                                                
    print(f"\nShape di risultati['Am'] \033[1mconsiderando tutti i canali\033[0m: {risultati['Am'].shape}")  
    
    #Itero sul livello i-esimo di ricostruzione
    
    for i, livello in enumerate(livelli_di_decomposizione):
        max_level = np.max(livelli_di_decomposizione)
        print(f"max level is \033[1m{max_level}\033[0m")

        # Sapendo che risultati['Am'] abbia dimensioni: (num_canali, num_samples, num_livelli)...

        '''OLD DEBUGGING
        #print(f"Livello: {livello}")  # Debugging
        #print(f"\nForma risultati['Am'] \033[1mconsiderando tutti i canali\033[0m: {risultati['Am'].shape}")  # Debugging
        '''

        # Allora, la Shape di Am_livello sarà 
        #(num_canali, num_samples) per il livello corrente
                                    
        Am_livello = risultati['Am'][canali_di_interesse, :, livello]

        '''OLD DEBUGGING
        #print(f"Forma Am_livello: {Am_livello.shape}")  # Debugging
        '''
        
        '''OLD DEBUGGING
        # Debugging dettagliato
        # print(f"Condizione: {condizione}, Livello: {livello + 1}")
        '''

        '''DEBUGGING'''
        # Debugging dettagliato
        print(f"\nCondizione: \033[1m{condizione}\033[0m, Livello: \033[1m{livello + 1}\033[0m, Indice livello: \033[1m{livello}\033[0m")
        #print(f"Indice livello: \033[1m{livello}\033[0m")
        
        print(f"\nForma Am \033[1mper ogni livello\033[0m: {Am_livello.shape}")  # Debugging
        #print(f"Am forma: \033[1m{risultati['Am'].shape}\033[0m")

        # Ora, per ogni indice relativo ad un canale EEG...
        
        for ch_idx, ch in enumerate(canali_di_interesse):

            #Mi stampo il valore dei primi di 5 campioni associato ai canali EEG 
            #presi in esame durante l'ispezione visuale dei loro valori di voltaggio in μV 
            
            print(f"Canale: \033[1m{nomi_canali[ch_idx]}\033[0m, Dati: {Am_livello[ch_idx, :5]}")  # Stampa i primi 5 campioni per verifica
            
            # Scegli l'asse giusto
            ax = axs[ch_idx, i]
            
            # Plot delle ricostruzioni per il canale corrente
            ax.plot(asse_x_ms, Am_livello[ch_idx, :], color=colore, alpha=0.7, label=f'{condizione}')
            
            ax.set_title(f'Livello {livello + 1} - Canale {nomi_canali[ch_idx]}')
            if i == 0:
                ax.set_ylabel(f'Voltaggio (µV)')
            if ch_idx == len(canali_di_interesse) - 1:
                ax.set_xlabel('Tempo (mms)')

            # Aggiungi una linea verticale per indicare il periodo di pre-stimolo
            ax.axvline(x=0, color='black', linestyle='--')  # 0 ms corrisponde all'inizio del pre-stimolo

# Aggiungi le legende fuori dai plot
handles, labels = [], []
for ax in axs.flatten():
    for handle, label in zip(*ax.get_legend_handles_labels()):
        if label not in labels:
            handles.append(handle)
            labels.append(label)

# Prova a mettere la legenda dentro la figura, in alto a sinistra
fig.legend(handles, labels, loc='upper center', bbox_to_anchor=(0.5, 0.05), ncol=4, fontsize='large')

plt.tight_layout(rect=[0, 0.08, 1, 0.95])  # Aggiunge spazio per il titolo e la legenda
plt.show()

#fig.savefig('/home/stefano/Interrogait/Analyses_EEG_1_20/ricostruzione_coefficienti_approssimazione_terapista1.png', bbox_inches='tight')


## STEP 4.3.2.2 Discrete Wavelet Analysis (1-DWT): Example All Therapists & All Patients

#### **All experimental conditions** for all levels of decompositions: Description

##### NOTA BENE 
In questo caso, ottengo una **ricostruzione media globale** (i.e., su tutti i soggetti!) per **ogni livello di decomposizione**, andando a **raggruppare i dati per condizione sperimentale** 

<br>

Quando **ricostruisci il segnale dal dominio delle wavelet al dominio del tempo**, 
per un determinato livello di decomposizione, **utilizzi i coefficienti di approssimazione e dettaglio come segue**:

<br>


- **Coefficiente di Approssimazione dell'Ultimo Livello Considerato**:
  Questo è il coefficiente di approssimazione per l'ultimo livello di decomposizione
  che stai considerando. In altre parole, se stai ricostruendo il segnale al Livello 3,
  userai il coefficiente di approssimazione corrispondente al Livello 3.

- **Coefficienti di Dettaglio per i Livelli Superiore**:
  Utilizzerai i coefficienti di dettaglio per i livelli che sono superiori all'ultimo livello di decomposizione considerato.
  Ad esempio, se stai ricostruendo il segnale per il Livello 2, userai i coefficienti di dettaglio per il Livello 1 e il
  Livello 2.

<br>


- **Dettagli della Ricostruzione** Quando ricostruisci per un certo livello di decomposizione:

  - **Per il Livello 3**: Usa il coefficiente di approssimazione del Livello 3 ed Usa i coefficienti di dettaglio dei
    Livelli 1, 2 e 3.
  - **Per il Livello 2**: Usa il coefficiente di approssimazione del Livello 2 ed Usa i coefficienti di dettaglio dei
    Livelli 1 e 2.

<br>

- **Applicazione Pratica**
Am e Dm: Questi rappresentano i coefficienti medi di approssimazione e dettaglio rispettivamente,
calcolati su tutti i trial e canali per ogni condizione sperimentale.

Se **consideri un certo livello di decomposizione**, Am e Dm verranno presi dal livello di decomposizione corrispondente.

Per un livello specifico, 
- **Am** sarà il coefficiente di approssimazione dell'ultimo livello di decomposizione considerato e
- **Dm** sarà il coefficiente di dettaglio per i livelli fino a quello specificato.


<br>

#### Calcolo delle medie per **All experimental conditions** for all levels of decompositions

Le medie vengono calcolate in modo specifico per:

- Condizione Sperimentale: Ogni condizione sperimentale (come 'baseline', 'th_resp', 'vision_resp', 'shared_resp') viene trattata separatamente. Questo assicura che i dati siano concatenati e mediati solo all'interno della stessa condizione.

- Canale: La concatenazione e la media sono effettuate per ciascun canale separatamente. Questo significa che i dati per il canale 1, ad esempio, non si mescolano con quelli di un altro canale.

- Livello di Decomposizione: La media è calcolata per ogni livello di decomposizione in modo separato, mantenendo la struttura dei coefficienti di dettaglio (D) e approssimazione (A) distinti per ciascun livello.

<br>

Come Funziona:

- Concatenazione per Condizione: I coefficienti di dettaglio (D) e approssimazione (A) per tutti i trial di tutti i soggetti vengono concatenati per una specifica condizione sperimentale.

- Media su Tutti i Trial: Dopo la concatenazione, viene calcolata la media sui trial concatenati, ottenendo la ricostruzione media del segnale per ogni canale e livello di decomposizione, specifica per la condizione sperimentale in questione.

Questo approccio assicura che le medie riflettano accuratamente i dati della stessa condizione sperimentale, senza mescolare informazioni tra condizioni, canali o livelli diversi.


#### **All experimental conditions** for all levels of decompositions



In [ ]:
!pwd

In [ ]:
#Verifico che ogni dizionario dei dati di ogni soggetto abbia sia dati che labels 


therapists_data[-1].keys()

In [ ]:
''' PROVA 09/09/2024 POMERIGGIO - CALCOLO DI MEDIA GLOBALE e DEVIAZIONE STANDARD & LABELS - ALL SUBJECTS TH -1D-DWT'''

import numpy as np
import pywt

# Calcola il livello massimo di decomposizione
max_decomposition_level = pywt.dwtn_max_level((300,), 'db4')
level = max_decomposition_level  # Livello di decomposizione della wavelet
wavelet = 'db4'  # Tipo di wavelet da utilizzare

def compute_coefficients_per_level(signal, wavelet, max_level):
    '''Calcola i coefficienti di approssimazione e dettaglio per ogni livello di decomposizione'''
    all_coeffs = []
    for l in range(1, max_level + 1):
        coeffs = pywt.wavedec(signal, wavelet, level=l)
        all_coeffs.append(coeffs)
    return all_coeffs

def discrete_wavelet(EEG_data, level, wavelet, subject_idx):
    '''
    Cicla su tutti i trial (di ogni condizione sperimentale) di ogni canale ed esegue la DWT analysis
    '''
    num_trials, num_channels, num_samples = EEG_data.shape
    lev_check = int(np.floor(np.log2(num_samples)))
    if level > lev_check:
        print(f"max level of decomposition was exceeded!")
    else:
        print(f"\033[1mMax Level of decomposition\033[0m corresponds to the one calculated, which is \033[1m{level}\033[0m\n\n")

    # Dimensioni per C e L
    C = np.empty((num_trials, num_channels, level), dtype=object)
    L = np.empty((num_trials, num_channels, level), dtype=object)

    # Prepariamo array per i coefficienti di dettaglio e approssimazione
    D = np.zeros((num_trials, num_channels, num_samples, level))
    A = np.zeros((num_trials, num_channels, num_samples, level))

    # Per ogni trial e canale
    for tr in range(num_trials):
        for ch in range(num_channels):
            coeffs_all_levels = compute_coefficients_per_level(EEG_data[tr, ch, :], wavelet, level)
            trial_C = []
            trial_L = []

            for l, coeffs in enumerate(coeffs_all_levels):
                trial_C.append(coeffs)
                trial_L.append([len(c) for c in coeffs])

                # Ricostruzione del segnale con solo i coefficienti di dettaglio per il livello l
                D[tr, ch, :, l] = pywt.waverec(
                    [np.zeros_like(coeffs[0]) if i == 0 else (coeffs[i] if i == l + 1 else np.zeros_like(coeffs[i]))
                     for i in range(len(coeffs))], wavelet)

                # Ricostruzione del segnale con solo i coefficienti di approssimazione per il livello l
                A[tr, ch, :, l] = pywt.waverec(
                    [coeffs[0] if i == 0 else np.zeros_like(coeffs[i])
                     for i in range(len(coeffs))], wavelet)

            C[tr, ch] = trial_C
            L[tr, ch] = trial_L

    # Crea il nome dinamico per la struttura wave_subj_X
    wave_subj_name = f'wave_subj_{subject_idx}'
    
    wave_subj = {
        'C': C,
        'L': L,
        'D': D,
        'A': A,
    }

    return wave_subj_name, wave_subj

def process_all_subjects(therapists_data, level, wavelet):
    
    # Dizionario per memorizzare i risultati separati per condizione sperimentale
    condition_results = {}

    # Itera sui dizionari nella lista
    for idx, data_dict in enumerate(therapists_data):
        print(f"\n\n\t\t\t\t\t\033[1mProcessing Subject {idx + 1}\033[0m:\n")
        
        for condition, value in data_dict.items():
            if '_labels' in condition:
                base_condition = condition.replace('_labels', '')  # Rimuove '_labels'
                condition_key = base_condition
                labels_key = condition
            else:
                base_condition = condition
                condition_key = base_condition
                labels_key = f'{base_condition}_labels'

            # Inizializza la chiave se non esiste e se non è una chiave con '_labels'
            if '_labels' not in condition and condition_key not in condition_results:
                condition_results[condition_key] = {'D': [], 'A': [], 'A_labels': []}

            # Gestisci i dati e le etichette
            if isinstance(value, np.ndarray):  # Verifica se il valore è un np.array
                print(f"\nApplicazione wavelet per '\033[1m{condition_key}\033[0m'\n")
    
                # Stampa la forma dei dati per la condizione e soggetto corrente
                print(f"\033[1mShape\033[0m dei dati per \033[1m{condition_key}\033[0m: {value.shape}")
    
                # Applica la wavelet e ottieni i risultati con il nome dinamico per il soggetto
                wave_subj_name, wave_subj = discrete_wavelet(value, level, wavelet, idx + 1)
                
                # Salva i coefficienti per la condizione corrente
                condition_results[condition_key]['D'].append(wave_subj['D'])
                condition_results[condition_key]['A'].append(wave_subj['A'])
                
                # Gestisci le etichette
                if labels_key in data_dict:
                    num_labels = data_dict[labels_key]
                    if condition_key in condition_results:
                        
                        #print(f"Found labels for condition \033[1m{condition_key}\033[0m")
                        print(f"Found labels for condition \033[1m{labels_key}\033[0m, whose length is \033[1m{len(num_labels)}\033[0m\n")
                        condition_results[condition_key]['A_labels'].extend(num_labels)
            else:
                print(f"\033[1m{labels_key}\033[0m' non è un np.array, non applicare la wavelet")
                
    # Per ciascuna condizione, concatena i risultati su tutti i soggetti e calcola le medie e deviazioni standard
    all_subjects_condition_results = {}
    
    for condition_key, results in condition_results.items():
        if "_labels" in condition_key or not results['D'] or not results['A']:
            print(f"\nSkipping \033[1m{labels_key}\033[0m as it appears to be a \033[1mlabel\033[0m or has \033[1mno valid data\033[0m.")
            continue

        wave_condition_name = f'wave_{condition_key}'
        
        print(f"\n\nResults for \t\t\t\t\t\033[1m{wave_condition_name}\033[0m:\n\n")
        
        # Concatenazione per canale, livello, su tutti i soggetti
        D_concatenated = np.concatenate(results['D'], axis=0)  # Concatenazione su tutti i trial e soggetti
        A_concatenated = np.concatenate(results['A'], axis=0)  # Concatenazione su tutti i trial e soggetti

        # Calcola la media e la deviazione standard su tutti i trial della stessa condizione sperimentale, per ciascun livello e canale
        Dm = np.mean(D_concatenated, axis=0)  # Media sui trial concatenati
        Am = np.mean(A_concatenated, axis=0)  # Media sui trial concatenati
        D_std = np.std(D_concatenated, axis=0)  # Deviazione standard sui trial concatenati
        A_std = np.std(A_concatenated, axis=0)  # Deviazione standard sui trial concatenati

        # Crea il dizionario finale per la condizione
        wave_condition = {
            'D': D_concatenated,
            'A': A_concatenated,
            'Dm': Dm,
            'Am': Am,
            'D_std': D_std,
            'A_std': A_std,
            'A_labels': results['A_labels']  # Aggiunta del numero di etichette specifiche per A
        }

        print(f"\n\nResults for \033[1m{wave_condition_name}\033[0m:")
        print(f"D shape before mean for the condition \033[1m'{condition_key}'\033[0m: {D_concatenated.shape}")
        print(f"A shape before mean for the condition \033[1m'{condition_key}'\033[0m: {A_concatenated.shape}")
        print(f"Dm shape for condition \033[1m'{condition_key}'\033[0m after mean: {Dm.shape}")
        print(f"Am shape for condition \033[1m'{condition_key}'\033[0m after mean: {Am.shape}")
        print(f"D_std shape for condition \033[1m'{condition_key}'\033[0m after std: {D_std.shape}")
        print(f"A_std shape for condition \033[1m'{condition_key}'\033[0m after std: {A_std.shape}")
        
        # Salva i risultati nel dizionario delle condizioni
        all_subjects_condition_results[wave_condition_name] = wave_condition

    return all_subjects_condition_results


In [ ]:
# Richiamo della funzione per processare tutti i soggetti e ottenere i risultati per ciascuna condizione
all_subjects_condition_results_th = process_all_subjects(therapists_data, level, wavelet)

In [ ]:
#len(patients_data) 
#output : 15

#patients_data[0].keys()
#output : dict_keys(['baseline_1', 'vision_resp_1', 
                    #'th_resp_1', 'shared_resp_1', 
                    #'baseline_1_labels', 'vision_resp_1_labels',
                    #'th_resp_1_labels', 'shared_resp_1_labels'])

#patients_data[0].keys()

In [ ]:
all_subjects_condition_results_pt = process_all_subjects(patients_data, level, wavelet)

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
!pwd

In [ ]:
#Salvo ricostruzioni 4° e 5° livello terapisti

''' PATH  --> cd Plots_Sliding_Estimator_MNE '''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('all_subjects_condition_results_th.pkl', 'wb') as f:
#    pickle.dump(all_subjects_condition_results_th, f)
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_subjects_condition_results_th.pkl', 'wb') as f:
    pickle.dump(all_subjects_condition_results_th, f)

In [ ]:
#Salvo ricostruzioni 4° e 5° livello pazienti

''' PATH  --> cd Plots_Sliding_Estimator_MNE'''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('new_all_subjects_condition_results_pt.pkl', 'wb') as f:
#    pickle.dump(all_subjects_condition_results_pt, f)
    
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_subjects_condition_results_pt.pkl', 'wb') as f:
    pickle.dump(all_subjects_condition_results_pt, f)

## STEP 4.3.2.3 Discrete Wavelet Analysis (2-DWT): Example All Therapists & All Patients

#### **Spiegazione di 2D DWT**

Per capire meglio la struttura delle **matrici** "**D_concatenated**" e "**A_concatenated**" e come ci si arriva, occorre approfondire il funzionamento di wavedec2 e la struttura dei dati che restituisce. Analizziamo il processo in dettaglio:


##### **1. Cosa fa wavedec2?**
**wavedec2** è una funzione per la **decomposizione wavelet bidimensionale (2D)** utilizzata principalmente per analisi di immagini o segnali 2D. Per un'immagine o un array bidimensionale in input:

- Livello 1:

    Decomposizione in 
    - **Coefficienti di approssimazione** (scala bassa risoluzione) e
    - **Coefficienti di dettaglio** suddivisi in **tre direzioni**:
       - Orizzontale (**H**)
       - Verticale (**V**)
       - Diagonale (**D**)
    
    <br>
    
    Questo significa che il **livello 1** restituisce:
    - Un **array** per i coefficienti di approssimazione (A1),
    - Una **tupla con tre array** per i coefficienti di dettaglio: ((H1, V1, D1)).

<br>

- Livelli successivi:

    - La decomposizione si applica ulteriormente sui coefficienti di approssimazione generati al livello precedente.
    - Per il **livello N**, otterrai:
      - I **coefficienti di approssimazione** ridotti A_N (array bidimensionale),
      - Una **tupla con tre array** per i coefficienti di dettaglio di ciascun livello: ((H_N, V_N, D_N)).
     
     <br>
     
     Esempio: Se applichi una decomposizione a due livelli (level = 2) su un array 2D di shape (256, 256):

<br>
    
- Livello 1:

 - A1: Coefficienti di approssimazione, shape (128, 128)
 - H1, V1, D1: Coefficienti di dettaglio, shape (128, 128) ciascuno.

<br>
    
- Livello 2:

 - A2: Coefficienti di approssimazione, shape (64, 64)
 - H2, V2, D2: Coefficienti di dettaglio, shape (64, 64) ciascuno.

<br>


##### **2. Come vengono utilizzati i coefficienti nel codice?**

Nel contesto del codice:

- Coefficienti di dettaglio (D):
    - Viene costruito un **array D** che **concatena** i **coefficienti di dettaglio su tutte le direzioni (H, V, D) per tutti i livelli e per tutti i trial**.

- Coefficienti di approssimazione (A):
    - Viene costruito un **array A** che raccoglie i **coefficienti di approssimazione finali (dopo tutti i livelli) per ogni trial**.


<br>


##### **3. Shape di D_concatenated e A_concatenated**
La **shape** di queste matrici *dipende* dal **numero di trial**, dal **numero di livelli** e dalla **risoluzione dei dati**:

- **D_concatenated**

**Ogni trial** contribuisce con **un array di coefficienti di dettaglio**. 

Se ci sono N trial, **i coefficienti concatenati di tutti i livelli e tutte le direzioni** avranno questa shape:
        
        (numero trial, somma delle dimensioni di 𝐻,𝑉,𝐷 per ogni livello)

Ad esempio:

Trial di input con shape (256, 256) e decomposizione su 2 livelli:
Livello 1: H1, V1, D1 -> shape (128, 128) ciascuno.
Livello 2: H2, V2, D2 -> shape (64, 64) ciascuno.

Somma totale delle dimensioni: 3 × (128×128) + 3 × (64×64).

Per N trial: 𝑁 × somma totale dimensioni dettagli N×somma totale dimensioni dettagli.

- **A_concatenated**

**Ogni trial** contribuisce con **un array di coefficienti di approssimazione finale**. Se ci sono N trial:
            
        (numero trial , dimensioni dei coefficienti di approssimazione finali)


Ad esempio:

Trial di input con shape (256, 256) e decomposizione su 2 livelli:
Coefficienti di approssimazione finali (A2): shape (64, 64).
Per N trial: N×(64×64).


##### **4. Shape risultante: ricostruzione del 2D**
La ricostruzione completa 2D per ogni trial (sommando dettagli e approssimazione) richiede di:

- Sommare i coefficienti di approssimazione e dettaglio per ogni livello.
- Ricostruire la matrice originale usando waverec2.
- Se vuoi ottenere una matrice "finale" per ogni condizione sperimentale (concatenando i trial di tutti i soggetti):

Dimensione finale D: (numero totale di trial, somma totale delle dimensioni di dettaglio per livello, 


Dimensione finale A: (numero totale di trial, dimensioni di approssimazione finale)

#####  **Conclusione**
Se vuoi una ricostruzione completa, devi lavorare con i coefficienti concatenati e ricostruire l'immagine (trial 2D) con waverec2. 

La concatenazione D_concatenated e A_concatenated ti serve principalmente per l'analisi statistica su più trial.

Se hai dei dati specifici, possiamo fare un esempio concreto per verificare queste shape!


<br>

##### ***OUTPUT CODICE***

Il codice da in output, per ciascuna condizione sperimentale, 
per ogni livello di decomposizione, 
una concatenazione della ricostruzione sottoforma di immagine, di ogni trial, rispetto al livello che considero, ossia:

**D_concatenated** rappresenta in sostanza, per ciascuno dei livelli che considero, 
la ricostruzione di ogni trial rispetto a quella condizione sperimentale corrente

**A_concatenated**, allo stesso modo, è organizzato in maniera analoga.

Con il codice attuale, D_concatenated e A_concatenated quindi rappresentano
la concatenazione delle ricostruzioni rispettivamente per i coefficienti di dettaglio e di approssimazione, 
e sono organizzati in modo che ogni riga (o primo indice) rappresenti un trial.


##### **5. Shape risultante: ricostruzione del 2D: Cosa contengono D_concatenated e A_concatenated**

- **D_concatenated**: Contiene le ricostruzioni dei coefficienti di dettaglio per tutti i trial di una data condizione sperimentale, su tutti i livelli di decomposizione.

- **A_concatenated**: Contiene le ricostruzioni dei coefficienti di approssimazione, sempre per tutti i trial della stessa condizione sperimentale.
Questi array includono quindi una ricostruzione bidimensionale per ogni trial usando solo i coefficienti corrispondenti a ciascun livello.


Come sono strutturati

Supponiamo di avere:

- num_trials = 100 (trials per condizione sperimentale),
- num_channels = 64 (canali EEG),
- num_samples = 300 (punti temporali per trial),
- level = 4 (livelli di decomposizione).

Allora:

- Prima della concatenazione:
    D[tr, :, :, l] contiene la ricostruzione 2D per il livello l del trial tr. Stesso vale per A[tr, :, :, l].

- Dopo la concatenazione (np.concatenate):
    
    - D_concatenated avrà dimensione (num_trials, num_channels, num_samples, level):
       - num_trials → numero totale di trial,
       - num_channels → numero di canali EEG,
       - num_samples → numero di punti temporali,
       - level → livelli di decomposizione.
    
    - A_concatenated segue la stessa struttura.


<br>


**Per il punto ##### 4. Shape risultante: ricostruzione del 2D**


Per la concatenazione io avrò,

per **ogni soggetto**, per **ogni condizione sperimentale**, per **ogni livello** (che sia dei coefficienti di dettaglio o di approssimazione, separatamente ovviamente!), 

la **concatenazione delle ricostruzioni, dell'i-esimo livello, rispetto ai coefficienti di dettaglio o di approssimazione (D_concatanated o A_concatenated) di ogni trial della specifica condizione sperimantale**, giusto?

<br>

Per chiarire meglio:

- **Per ogni soggetto, condizione sperimentale e livello**:
  - **D_concatenated**: Sarà la concatenazione, lungo l'asse dei trial, delle ricostruzioni 2D basate **esclusivamente sui 
    coefficienti di dettaglio** (ad esempio, per il livello 𝑙, solo i coefficienti **𝐷𝑙**)
    
  - **A_concatenated**: Sarà la concatenazione, lungo l'asse dei trial, delle ricostruzioni 2D basate **esclusivamente sui 
    coefficienti di approssimazione** (ad esempio, per il livello 𝑙, solo i coefficienti **𝐴𝑙**)

<br>

Forma risultante:

- **Dimensione di D_concatenated**:
    - Ogni matrice ricostruita dal dettaglio per un trial avrà dimensioni (𝑛𝑢𝑚_𝑐ℎ𝑎𝑛𝑛𝑒𝑙𝑠, 𝑛𝑢𝑚_𝑠𝑎𝑚𝑝𝑙𝑒𝑠)
    - Dopo la concatenazione di tutti i trial di una condizione sperimentale, si otterrano array di dimensione 
      (numero totale di trial,num_channels,num_samples)

- **A_concatenated**: 
    - Ogni matrice ricostruita dall'approssimazione per un trial avrà anch'essa dimensioni (𝑛𝑢𝑚_𝑐ℎ𝑎𝑛𝑛𝑒𝑙𝑠, 𝑛𝑢𝑚_𝑠𝑎𝑚𝑝𝑙𝑒𝑠)
    - Dopo la concatenazione di tutti i trial di una condizione sperimentale, si otterrano array di dimensione 
      (numero totale di trial,num_channels,num_samples)
      
<br>

Per ciascun livello:

- Il **processo di ricostruzione** viene applicato **separatamente per ogni livello**
- Di conseguenza, per ogni livello 𝑙, avrai:

   - Un D_concatenated che rappresenta la concatenazione delle ricostruzioni basate sui dettagli del livello 𝑙
   - Un A_concatenated che rappresenta la concatenazione delle ricostruzioni basate sull'approssimazione del livello 𝑙
   
<br>

Organizzazione nei risultati finali:

Nel dizionario condition_results (o all_subjects_condition_results), i dati saranno organizzati in questo modo:


- **Per ogni condizione sperimentale**:

  - 'D': contiene un array 3D (dopo la concatenazione) dei dettagli per ciascun livello
  
  - 'A': contiene un array 3D (dopo la concatenazione) delle approssimazioni per ciascun livello
  
  - 'A_labels': contiene le etichette associate ai trial concatenati
  
  
<br>

Conclusione:

Con questa struttura, puoi accedere direttamente alle ricostruzioni concatenated dei coefficienti di dettaglio (D_concatenated) o di approssimazione (A_concatenated) per qualsiasi condizione sperimentale, livello e trial.


#### **2D Wavelet Functions**

1) **pywavelets.wavedec2**

2D multilevel decomposition using wavedec2
pywt.wavedec2(data, wavelet, mode='symmetric', level=None, axes=(-2, -1))
Multilevel 2D Discrete Wavelet Transform.

        Parameters: 
        
        data: ndarray
            2D input data

        wavelet: Wavelet object or name string, or 2-tuple of wavelets
            Wavelet to use. This can also be a tuple containing a wavelet to apply along each axis in axes.

        mode: str or 2-tuple of str, optional
            Signal extension mode, see Modes. This can also be a tuple containing a mode to apply along each axis in 
            axes.

        level: int, optional 
            Decomposition level (must be >= 0). If level is None (default) then it will be calculated using the 
            dwt_max_level function.

        axes: 2-tuple of ints, optional
            Axes over which to compute the DWT. Repeated elements are not allowed.

        Returns: [cAn, (cHn, cVn, cDn), … (cH1, cV1, cD1)]: list
        
        Coefficients list. 
        For user-specified axes, cH* corresponds to axes[0] while cV* corresponds to axes[1]. 
        The first element returned is the approximation coefficients for the nth level of decomposition. 
        
        Remaining elements are tuples of detail coefficients in descending order of decomposition level. (i.e. cH1 are the 
        horizontal detail coefficients at the first level)
        
        
2) **pywavelets.waverec2** (https://pywavelets.readthedocs.io/en/latest/ref/2d-dwt-and-idwt.html#pywt.waverec2)

pywt.waverec2(coeffs, wavelet, mode='symmetric', axes=(-2, -1))
Multilevel 2D Inverse Discrete Wavelet Transform.

        Parameters: 
        
        coeffs: list or tuple
            Coefficients list [cAn, (cHn, cVn, cDn), … (cH1, cV1, cD1)]

        wavelet: Wavelet object or name string, or 2-tuple of wavelets
            Wavelet to use. This can also be a tuple containing a wavelet to apply along each axis in axes.

        mode: str or 2-tuple of str, optional
            Signal extension mode, see Modes. This can also be a tuple containing a mode to apply along each axis in 
            axes.

        axes: 2-tuple of ints, optional
            Axes over which to compute the DWT. Repeated elements are not allowed.

        Returns: [cAn, (cHn, cVn, cDn), … (cH1, cV1, cD1)]: list
        
        Coefficients list. For user-specified axes, cH* corresponds to axes[0] while cV* corresponds to axes[1]. 
        The first element returned is the approximation coefficients for the nth level of decomposition. 
        
        Remaining elements are tuples of detail coefficients in descending order of decomposition level. (i.e. cH1 are the 
        horizontal detail coefficients at the first level)

        
        Notes

        It may sometimes be desired to run waverec2 with some sets of coefficients omitted. This can best be done by 
        setting the corresponding arrays to zero arrays of matching shape and dtype. Explicitly removing list or tuple 
        entries or setting them to None is not supported.

        Specifically, to ignore all detail coefficients at level 2, one could do:

        coeffs[-2] == tuple([np.zeros_like(v) for v in coeffs[-2]])

#### Implementation of **2D Discrete Wavelet Transform: Comparsa ERRORI utili per il codice: LEGGERE!** 

Quando eseguo la funzione, mi compare un **errore** rispettp a questa parte di codice:

        for l, coeffs in enumerate(coeffs_all_levels):

                    '''IN QUESTO CASO NON POSSO SAPERE LA LUNGHEZZE/SHAPE DEI COEFF APPROX E DETAIL 
                    ALLO STESSO MODO,

                    #trial_C.append(coeffs)
                    #trial_L.append([c.shape for c in coeffs])

                    DATO CHE 

                    - APPROX COEFF = NP.ARRAY,
                    - APPROX DETAIL = TUPLE (NP.ARRAY, NP.ARRAY, NP.ARRAY), CIASCUNO PER LE 3 DIREZIONI

                    QUI SOTTO INVECE VIENE RIPORTATO IL MODO CORRETTO DI STAMPARE LE SHAPE        

                    '''

                    # Gestisci separatamente la forma della matrice di approssimazione e dei dettagli
                    approx_shape = coeffs[0].shape  # Forma della matrice di approssimazione
                    detail_shapes = [detail.shape for detail in coeffs[1]]  # Forme dei dettagli
                    trial_L.append((approx_shape, detail_shapes))  # Salva entrambe le forme


                    # Ricostruzione del segnale con solo i coefficienti di dettaglio per il livello l
                    D[tr, :, :, l] = pywt.waverec2(
                        # Modifica: isoliamo solo i coefficienti di dettaglio
                        (np.zeros_like(coeffs[0]), tuple(
                            coeff if i == l - 1 else np.zeros_like(coeff) 
                            for i, coeff in enumerate(coeffs[1])
                        )),
                        wavelet
                    )

                    # Ricostruzione del segnale con solo i coefficienti di approssimazione per il livello l
                    A[tr, :, :, l] = pywt.waverec2(
                        # Modifica: isoliamo solo i coefficienti di approssimazione
                        (coeffs[0], tuple(
                            np.zeros_like(coeff) for coeff in coeffs[1]
                        )),
                        wavelet
                    )
    
<br>

In cui si dice:


                ---------------------------------------------------------------------------
                ValueError                                Traceback (most recent call last)
                Cell In[101], line 2
                      1 # Richiamo della funzione per processare tutti i soggetti e ottenere i risultati per ciascuna 
                      condizione
                ----> 2 all_subjects_condition_results_th = process_all_subjects_2D(therapists_data, level, wavelet)

                Cell In[100], line 185, in process_all_subjects_2D(therapists_data, level, wavelet)
                    182 print(f"\nApplicazione wavelet per '\033[1m{condition_key}\033[0m'\n")
                    183 print(f"\033[1mShape\033[0m dei dati per \033[1m{condition_key}\033[0m: {value.shape}")
                --> 185 wave_subj_name, wave_subj = discrete_wavelet_2D(value, level, wavelet, idx + 1)
                    187 # Modifica: Aggiungi dati 2D al dizionario
                    188 condition_results[condition_key]['D'].append(wave_subj['D'])

                Cell In[100], line 124, in discrete_wavelet_2D(EEG_data, level, wavelet, subject_idx)
                    120 trial_L.append((approx_shape, detail_shapes))  # Salva entrambe le forme
                    123 # Ricostruzione del segnale con solo i coefficienti di dettaglio per il livello l
                --> 124 D[tr, :, :, l] = pywt.waverec2(
                    125     # Modifica: isoliamo solo i coefficienti di dettaglio
                    126     (np.zeros_like(coeffs[0]), tuple(
                    127         coeff if i == l - 1 else np.zeros_like(coeff) 
                    128         for i, coeff in enumerate(coeffs[1])
                    129     )),
                    130     wavelet
                    131 )
                    133 # Ricostruzione del segnale con solo i coefficienti di approssimazione per il livello l
                    134 A[tr, :, :, l] = pywt.waverec2(
                    135     # Modifica: isoliamo solo i coefficienti di approssimazione
                    136     (coeffs[0], tuple(
                   (...)
                    139     wavelet
                    140 )

                ValueError: could not broadcast input array from shape (62,300) into shape (61,300)

<br>

Il problema deriva dalla **discrepanza nella forma del segnale ricostruito dalla funzione pywt.waverec2 rispetto alla dimensione attesa**. 

Questo **può accadere perché la trasformata wavelet 2D può modificare le dimensioni del segnale a seconda del livello di decomposizione e dei dettagli**. 

Ecco una spiegazione e come risolvere:

**1. Perché c'è una discrepanza nelle dimensioni?**
La trasformata wavelet 2D (**wavedec2**) e la successiva ricostruzione (**waverec2**) possono **introdurre variazioni nelle dimensioni**, perché **alcune wavelet** richiedono **padding dei dati per allineare correttamente il segnale**. 

**Ciò si traduce in un segnale ricostruito con dimensioni diverse rispetto all'originale**.

Nel tuo caso:

- Prima della ricostruzione, ò'input ha una dimensione di (61, 300).
- Dopo la ricostruzione, una dimensione è diventata 62 invece di 61!


**2. Come verificare e correggere il problema?**

Puoi fare quanto segue per gestire le dimensioni non corrispondenti:

- **Verifica delle forme**

Inserisci dei controlli per verificare la forma del segnale ricostruito e quella attesa. Ad esempio:

        reconstructed_D = pywt.waverec2(
            (np.zeros_like(coeffs[0]), tuple(
                coeff if i == l - 1 else np.zeros_like(coeff)
                for i, coeff in enumerate(coeffs[1])
            )),
            wavelet
        )

        # Stampa le forme per capire il problema
        print(f"Original shape: {signal_2D.shape}, Reconstructed D shape: {reconstructed_D.shape}")

<br>

- **Adattamento delle dimensioni**

Se le dimensioni non corrispondono, puoi adattare i dati ricostruiti utilizzando slicing o padding. Ad esempio:

    # Adatta le dimensioni per farle corrispondere
    if reconstructed_D.shape != signal_2D.shape:
        reconstructed_D = reconstructed_D[:signal_2D.shape[0], :signal_2D.shape[1]]


<br>

- **Modifica del codice**

Nel tuo codice, puoi integrare questa gestione nella ricostruzione dei coefficienti:

    # Ricostruzione del segnale con solo i coefficienti di dettaglio per il livello l
    reconstructed_D = pywt.waverec2(
        (np.zeros_like(coeffs[0]), tuple(
            coeff if i == l - 1 else np.zeros_like(coeff)
            for i, coeff in enumerate(coeffs[1])
        )),
        wavelet
    )

    # Adatta le dimensioni
    if reconstructed_D.shape != signal_2D.shape:
        reconstructed_D = reconstructed_D[:signal_2D.shape[0], :signal_2D.shape[1]]

    D[tr, :, :, l] = reconstructed_D
    
    
    reconstructed_A = pywt.waverec2(
    (coeffs[0], tuple(
        np.zeros_like(coeff) for coeff in coeffs[1]
    )),
    wavelet
    
    )

    if reconstructed_A.shape != signal_2D.shape:
        reconstructed_A = reconstructed_A[:signal_2D.shape[0], :signal_2D.shape[1]]

    A[tr, :, :, l] = reconstructed_A

<br>


**3. Possibili motivi del problema**

- Wavelet utilizzata: Alcune wavelet richiedono dimensioni specifiche dei dati. Puoi provare un'altra wavelet, come 'sym4', per vedere se il problema persiste.

- Livello di decomposizione: Livelli troppo alti rispetto alla forma originale possono causare problemi.


**4. Soluzione robusta**

- Integra sempre controlli per adattare i segnali ricostruiti alla dimensione originale e assicurati di testare diverse
  configurazioni di wavelet e livelli di decomposizione per trovare quella più adatta ai tuoi dati.


<br>


**IO**: 

Ok, come hai visto, io uso una **wavelet db4**.. per cui mi chiedo **in che modo il semplice "adattare" la shape della ricostruzione alla shape del segnale originale**, come mi hai suggerito tu qui 

    # Ricostruzione del segnale con solo i coefficienti di dettaglio per il livello l
    reconstructed_D = pywt.waverec2(
        (np.zeros_like(coeffs[0]), tuple(
            coeff if i == l - 1 else np.zeros_like(coeff)
            for i, coeff in enumerate(coeffs[1])
        )),
        wavelet
    )

    # Adatta le dimensioni
    if reconstructed_D.shape != signal_2D.shape:
        reconstructed_D = reconstructed_D[:signal_2D.shape[0], :signal_2D.shape[1]]

    D[tr, :, :, l] = reconstructed_D

    reconstructed_A = pywt.waverec2(
        (coeffs[0], tuple(
            np.zeros_like(coeff) for coeff in coeffs[1]
        )),
        wavelet
    )

    if reconstructed_A.shape != signal_2D.shape:
        reconstructed_A = reconstructed_A[:signal_2D.shape[0], :signal_2D.shape[1]]

    A[tr, :, :, l] = reconstructed_A

possa in qualche modo **impattare sulla qualità dell'immagine 2D** che io dovrei andare a fornire successivamente al mio classificatore di machine learning o di rete neurale...


<br>

**CHAT**: 


**Adattare** la forma delle ricostruzioni per conformarsi a quella del segnale originale **non altera in modo significativo** la qualità dell'immagine finale, **a patto che le modifiche siano minime**. 

Ecco alcune considerazioni chiave per capire l'impatto di questo approccio:


**1. Comportamento della Wavelet Transformation**

La wavelet db4 è una wavelet di Daubechies con quattro coefficienti. Questo tipo di wavelet ha un supporto relativamente lungo e richiede padding o troncamento per processare segnali con lunghezza non multipla della sua dimensione minima. Questo spiega perché le ricostruzioni possono risultare leggermente più grandi rispetto al segnale originale.

Cosa succede durante il "taglio"? Se la ricostruzione supera di poco la dimensione del segnale originale (ad esempio, hai una dimensione 62 anziché 61), tagliare l'eccesso elimina dati potenzialmente "inutili" introdotti dal padding. Questo è comune in analisi wavelet ed è progettato per preservare l'integrità del segnale.


**2. Impatto sul Classificatore**
I classificatori (machine learning o deep learning) sono tipicamente robusti rispetto a variazioni di scala o dimensione, a condizione che i dati forniti rispettino un formato coerente e informativo.

Qualità dell'immagine: Tagliare l'output alla dimensione originale non degrada significativamente il contenuto informativo dell'immagine, soprattutto se le modifiche avvengono su margini privi di informazioni importanti.
Informazioni locali: La wavelet lavora su scale e frequenze locali; l'informazione primaria resta intatta anche dopo l'adattamento delle dimensioni.


**3. Alternative al Troncamento**

Se sei preoccupato per un potenziale impatto negativo, puoi considerare un approccio alternativo:

- **Zero Padding**: Se la ricostruzione è più piccola dell'originale, puoi effettuare un padding con zeri per riportare il segnale alla forma corretta.

- **Rescaling**: Se il troncamento o il padding non è desiderabile, puoi interpolare o ridimensionare l'immagine finale usando metodi standard come bilinear interpolation o bicubic interpolation. Questo approccio è utile se i margini contengono informazioni che non vuoi perdere.

**4. Verifica dell'Impatto**

Puoi verificare se il troncamento ha un impatto rilevante confrontando la performance del tuo classificatore in due scenari:

- **Con troncamento**: Utilizzando i dati attuali (dimensioni adattate al segnale originale).
- **Senza troncamento**: Usando l'intera ricostruzione senza modifiche, oppure interpolando i dati al formato desiderato.

Se il classificatore produce risultati simili in entrambi i casi, l'approccio con troncamento è adeguato.


**5. Considerazioni Finali**

- Per wavelet come db4, la differenza nelle dimensioni è spesso insignificante dal punto di vista pratico.
- Se il tuo classificatore richiede input di dimensioni fisse, il troncamento è una scelta ragionevole, a meno che tu non noti un deterioramento significativo della performance.

**In sintesi, il semplice adattamento delle dimensioni non dovrebbe impattare negativamente la qualità del tuo input per il classificatore, soprattutto se le informazioni principali sono preservate e la modifica riguarda SOLO BORDI o MARGINI**.



<br>


**IO**: 

Quindi siccome mi hai detto che 

 "il semplice adattamento delle dimensioni non dovrebbe impattare negativamente la qualità del tuo input per il classificatore, soprattutto se le informazioni principali sono preservate e la modifica riguarda solo BORDI o MARGINI."

visto che il mio errore diceva

---------------------------------------------------------------------------
            ValueError                                Traceback (most recent call last)
            Cell In[101], line 2
                  1 # Richiamo della funzione per processare tutti i soggetti e ottenere i risultati per ciascuna 
                  condizione
            ----> 2 all_subjects_condition_results_th = process_all_subjects_2D(therapists_data, level, wavelet)

            Cell In[100], line 185, in process_all_subjects_2D(therapists_data, level, wavelet)
                182 print(f"\nApplicazione wavelet per '\033[1m{condition_key}\033[0m'\n")
                183 print(f"\033[1mShape\033[0m dei dati per \033[1m{condition_key}\033[0m: {value.shape}")
            --> 185 wave_subj_name, wave_subj = discrete_wavelet_2D(value, level, wavelet, idx + 1)
                187 # Modifica: Aggiungi dati 2D al dizionario
                188 condition_results[condition_key]['D'].append(wave_subj['D'])

            Cell In[100], line 124, in discrete_wavelet_2D(EEG_data, level, wavelet, subject_idx)
                120 trial_L.append((approx_shape, detail_shapes))  # Salva entrambe le forme
                123 # Ricostruzione del segnale con solo i coefficienti di dettaglio per il livello l
            --> 124 D[tr, :, :, l] = pywt.waverec2(
                125     # Modifica: isoliamo solo i coefficienti di dettaglio
                126     (np.zeros_like(coeffs[0]), tuple(
                127         coeff if i == l - 1 else np.zeros_like(coeff) 
                128         for i, coeff in enumerate(coeffs[1])
                129     )),
                130     wavelet
                131 )
                133 # Ricostruzione del segnale con solo i coefficienti di approssimazione per il livello l
                134 A[tr, :, :, l] = pywt.waverec2(
                135     # Modifica: isoliamo solo i coefficienti di approssimazione
                136     (coeffs[0], tuple(
               (...)
                139     wavelet
                140 )

            ValueError: could not broadcast input array from shape (62,300) into shape (61,300)

che indicava che c'era un errore rispetto ad una solo valore di differenza nella 1° dimensione (62 vs 61), presumo che adottare una logica di 'adattamento' delle dimensioni in questo caso non dovrebbe impattare sulla qualità dell'immagine, ossia della ricostruzione in 2D.. giusto?


cioè fare

    # Ricostruzione del segnale con solo i coefficienti di dettaglio per il livello l
    reconstructed_D = pywt.waverec2(
        (np.zeros_like(coeffs[0]), tuple(
            coeff if i == l - 1 else np.zeros_like(coeff)
            for i, coeff in enumerate(coeffs[1])
        )),
        wavelet
    )

    # Adatta le dimensioni
    if reconstructed_D.shape != signal_2D.shape:
        reconstructed_D = reconstructed_D[:signal_2D.shape[0], :signal_2D.shape[1]]

    D[tr, :, :, l] = reconstructed_D

    reconstructed_A = pywt.waverec2(
        (coeffs[0], tuple(
            np.zeros_like(coeff) for coeff in coeffs[1]
        )),
        wavelet
    )

    if reconstructed_A.shape != signal_2D.shape:
        reconstructed_A = reconstructed_A[:signal_2D.shape[0], :signal_2D.shape[1]]

    A[tr, :, :, l] = reconstructed_A


forse anche integrando questo print,

    # Stampa le forme per capire il problema
    print(f"Original shape: {signal_2D.shape}, Reconstructed D shape: {reconstructed_D.shape}")

per visualizzare comunque 'di quanto' è stato adattato, per avere una idea nel corso del processo...


<br>


**CHAT**:

Sì, esattamente! Il tuo approccio è logico e ben ponderato. Adattare le dimensioni in questo caso non dovrebbe impattare negativamente sulla qualità della ricostruzione, soprattutto considerando che la differenza è solo di una riga (da 62 a 61 nella prima dimensione) e che questa differenza è una conseguenza delle proprietà matematiche della trasformata wavelet.

- **Conferma sull'impatto minimo**

  - **Dettagli locali preservati**: La riduzione di una riga nella dimensione 2D (da 62 a 61) avviene probabilmente ai margini, dove le wavelet tendono a introdurre padding o calcoli approssimativi. Questo significa che il contenuto principale del segnale, situato nelle regioni centrali, non viene influenzato.
  
  - **Classificatore ML/DL**: I modelli di machine learning o reti neurali operano su rappresentazioni numeriche e non sono particolarmente sensibili a variazioni di forma di questo tipo, specialmente se le immagini o i segnali finali sono coerenti e informativi.
  
  
- **Soluzione Proposta**

Integrare una logica di adattamento come quella che hai indicato è perfettamente appropriato. Inoltre, il print che proponi è un'ottima idea per monitorare e comprendere meglio l'entità degli adattamenti durante il processo.

Ecco il frammento di codice con il print per verificare le differenze di dimensione:

    # Ricostruzione del segnale con solo i coefficienti di dettaglio per il livello l
    reconstructed_D = pywt.waverec2(
        (np.zeros_like(coeffs[0]), tuple(
            coeff if i == l - 1 else np.zeros_like(coeff)
            for i, coeff in enumerate(coeffs[1])
        )),
        wavelet
    )

    # Adatta le dimensioni
    if reconstructed_D.shape != signal_2D.shape:
        print(f"[Adattamento Dimensioni] Original shape: {signal_2D.shape}, Reconstructed D shape: {reconstructed_D.shape}")
        reconstructed_D = reconstructed_D[:signal_2D.shape[0], :signal_2D.shape[1]]

    D[tr, :, :, l] = reconstructed_D

    # Ricostruzione del segnale con solo i coefficienti di approssimazione per il livello l
    reconstructed_A = pywt.waverec2(
        (coeffs[0], tuple(
            np.zeros_like(coeff) for coeff in coeffs[1]
        )),
        wavelet
    )

    if reconstructed_A.shape != signal_2D.shape:
        print(f"[Adattamento Dimensioni] Original shape: {signal_2D.shape}, Reconstructed A shape: {reconstructed_A.shape}")
        reconstructed_A = reconstructed_A[:signal_2D.shape[0], :signal_2D.shape[1]]

    A[tr, :, :, l] = reconstructed_A


Dubbio su **pywt.dwtn_max_level**: 


**IO**

Quando gli chiedo "**il massimo livello di decomposizione**", gli devo fornire **la shape dei dati di input**, che è sempre (300,) dato che io considero la mia matrice rispetto all'**ULTIMA DIMENSIONE** che è quella del tempo dei dati (che son 300 campioni discretizzati EEG)...

Ora, **è giusto mettere questa shape** (i.e., **(300,)**) **ANCHE** per i dati quando vengono sottoposti **alla wavelet 2D** giusto? 

**CHAT**

Sì, se i tuoi dati EEG hanno la forma (300,), dove 300 è il numero di campioni temporali per ciascun canale, e stai applicando la trasformata wavelet discreta 2D su ogni trial (che avrà una forma di (num_channels, num_samples)), allora la shape dei dati che passi alla funzione di decomposizione wavelet 2D deve riflettere questa struttura.

La funzione **pywt.wavedec2 (che è utilizzata per la decomposizione wavelet bidimensionale**) richiede che i dati abbiano la forma (num_channels, num_samples), dove:

- num_channels rappresenta il numero di canali EEG,
- num_samples è il numero di campioni temporali per ciascun canale.

Quindi, quando passi i dati alla funzione discrete_wavelet_2D (come hai fatto nel tuo codice), la shape dei dati 2D deve essere corretta.

Nel tuo caso, la forma del segnale 2D sarà:

    signal_2D = EEG_data[tr, :, :]  # shape: (num_channels, num_samples)

Poiché num_samples è sempre 300 (i tuoi campioni EEG) e num_channels dipende dal numero di canali EEG che hai nei tuoi dati, la forma sarà qualcosa come (num_channels, 300) per ciascun trial. E questa forma è quella che passerai alla funzione di decomposizione wavelet pywt.wavedec2.

- Riassunto:

 - Se stai lavorando con dati EEG in cui ogni trial ha la forma (num_channels, 300), il tuo codice è corretto nel fornire questa forma alla funzione di decomposizione wavelet 2D.

 - Il parametro max_decomposition_level che calcola il massimo livello di decomposizione, deve utilizzare la dimensione dei dati temporali (300), che è giusto usare, in quanto stai operando sui campioni temporali.

- Quando esegui la wavelet 2D, la decomposizione avviene separatamente per ogni trial, e il numero di canali e campioni temporali è rispettato nella decomposizione.  Quindi, sì, è giusto passare la forma dei tuoi dati 2D (ad esempio (num_channels, 300)) quando applichi la wavelet 2D.

<br>

**IO**

Sì ma io mi chiedevo **se come argomento della funzione "pywt.dwtn_max_level"** io debba fornire **(300,)** **anche se poi dopo faccio la DWT 2D**.. giusto?

**CHAT**

Ah, capisco meglio la tua domanda ora!

Quando usi la funzione pywt.dwtn_max_level, il parametro che gli passi come argomento per la shape dei dati è la forma del tuo array di input. 
Tuttavia, la funzione dwtn_max_level si riferisce al massimo livello di decomposizione per una transformata wavelet discreta 2D (DWT 2D) che considera tutte le dimensioni dei tuoi dati, non solo una dimensione.

Nel caso di una matrice 2D, la funzione pywt.dwtn_max_level richiede una tupla che rappresenti la forma del tuo dato 2D. Quindi, nel caso di dati EEG, la forma che devi passare a dwtn_max_level deve essere una tupla che rappresenta sia i canali che i campioni temporali, cioè (num_channels, num_samples).

Nel tuo caso specifico, visto che il numero di campioni temporali è sempre 300, e supponendo che il numero di canali sia variabile (ad esempio num_channels), la forma che devi passare dovrebbe essere (num_channels, 300).

Esempio:

    max_decomposition_level = pywt.dwtn_max_level((num_channels, 300), 'db4')

**Perché questa forma (num_channels, 300)**?

La funzione dwtn_max_level calcola il massimo livello di decomposizione della wavelet in base alla dimensione minima tra i canali e i campioni temporali. Poiché la DWT 2D coinvolge la decomposizione sia per la dimensione temporale che per la dimensione spaziale (i canali), deve prendere in considerazione entrambe le dimensioni per determinare il massimo livello di decomposizione.

In pratica, quando usi dwtn_max_level, è corretto fornire la forma completa dei tuoi dati 2D, anche se successivamente applicherai una DWT 2D a ciascun trial (che utilizza la stessa forma).

**Conclusione**:

Sì, quando chiami pywt.dwtn_max_level, devi passare la forma completa (num_channels, num_samples) per calcolare correttamente il massimo livello di decomposizione, anche se successivamente applicherai la DWT 2D sui dati di ciascun trial.

<br>

**IO**

Ok, ma l'output mi dice che è 3... e siccome io ho i dati (300 punti) campionati a 250Hz, vuol dire che il massimo livello di decomposizione dei miei dati fino a che bande di frequenze arriva..?


**CHAT**

Il massimo livello di decomposizione che la funzione pywt.dwtn_max_level ti restituisce indica quante volte puoi decomporre i tuoi dati senza che la dimensione del segnale scenda sotto una certa soglia. Quando si esegue una decomposizione wavelet, ogni livello successivo dimezza la risoluzione in frequenza. In altre parole, una decomposizione successiva "comprime" sempre di più la finestra temporale e le bande di frequenza, riducendo la risoluzione temporale in favore di una risoluzione frequenziale più alta.

**Cosa significa "3" come livello massimo?**

Nel tuo caso, il massimo livello di decomposizione che ti restituisce è 3. Questo significa che puoi decomporre i tuoi dati fino a tre livelli, ma quando arrivi al quarto livello, la lunghezza dei dati risultanti sarebbe troppo piccola per poter applicare ulteriori decomposizioni. Quindi, dopo 3 livelli di decomposizione, la risoluzione temporale dei coefficienti sarebbe troppo bassa per essere utile.

**Riguardo alle bande di frequenze**:
Poiché i tuoi dati sono campionati a 250 Hz, la frequenza massima del tuo segnale è 125 Hz (secondo il teorema di Nyquist). Durante la decomposizione wavelet, ogni livello riduce la risoluzione temporale, ma permette una maggiore risoluzione in frequenza. In pratica, con ogni livello successivo:

- **Primo livello**: La frequenza di Nyquist per il primo livello (applicando la wavelet) sarebbe di circa 125 Hz (della tua finestra di 300 campioni). Questo livello cattura frequenze fino a circa la metà di quella frequenza, cioè circa 62,5 Hz.

- **Secondo livello**: Con il secondo livello di decomposizione, la risoluzione temporale si dimezza, e ora puoi catturare frequenze fino a circa 31,25 Hz.

- **Terzo livello**: Con il terzo livello di decomposizione, la risoluzione temporale continua a dimezzarsi, ma ora catturi frequenze fino a circa 15,625 Hz.

**In sintesi**:

- Livello 1: Fino a circa 62,5 Hz
- Livello 2: Fino a circa 31,25 Hz
- Livello 3: Fino a circa 15,625 Hz

Quindi, con il massimo livello di decomposizione pari a 3, stai catturando frequenze fino a 15,625 Hz. Questo potrebbe essere appropriato per analizzare le frequenze basse, ma non sarebbe sufficiente per catturare frequenze molto alte (ad esempio, nelle bande Gamma o altre frequenze superiori).

Se vuoi esplorare frequenze più alte, dovresti ridurre il livello massimo di decomposizione, ma ciò comporterebbe un sacrificio della risoluzione temporale.

**IO**

No quello che mi chiedo io è **se volessi esplorare frequenze più basse dei 15,625 Hz**, perché in realtà io sto indagando le frequenze delta e theta...


**CHAT**

Ah, ho capito! Se stai cercando di esplorare frequenze più basse, come le delta (1-4 Hz) e theta (4-8 Hz), con un massimo livello di decomposizione pari a 3, devi considerare come la decomposizione wavelet separa le frequenze ad ogni livello.

Ogni livello di decomposizione riduce la risoluzione temporale dei dati (in pratica "espande" la finestra temporale), ma permette di captare frequenze più basse. 
Con una DWT 2D, questo significa che i dettagli e le approssimazioni a frequenze più basse saranno catturati nei livelli più alti della decomposizione, e per frequenze ancora più basse, dovresti applicare più livelli di decomposizione.

Se il tuo massimo livello di decomposizione è 3 e stai cercando di esplorare frequenze molto basse (come delta e theta), il livello 3 può essere sufficiente, ma dipende dalla banda di frequenze specifica che stai cercando di analizzare.

**Considerazioni**:

- Bande di frequenza:
Le frequenze Delta (1-4 Hz) e Theta (4-8 Hz) si trovano nella parte più bassa dello spettro. Queste frequenze sono relativamente basse, quindi potresti voler esplorare almeno il livello 3, ma dopo il livello 3, la frequenza massima catturabile sarebbe di circa 15,625 Hz, il che è troppo alto per analizzare solo le frequenze Delta e Theta.
Frequenze basse nei livelli di decomposizione:

- Livello 1: Frequenze fino a 62,5 Hz.
- Livello 2: Frequenze fino a 31,25 Hz.
- Livello 3: Frequenze fino a 15,625 Hz.

Per frequenze Delta (1-4 Hz) e Theta (4-8 Hz), dovresti esaminare i coefficienti a bassa frequenza (approssimazioni), che generalmente si trovano nel primo livello di decomposizione.

**Cosa fare**:

Se hai già un livello massimo di decomposizione di 3, significa che stai esaminando frequenze fino a 15,625 Hz, ma per frequenze come delta e theta (che sono più basse), la DWT (ondelette discrete) ti permetterà comunque di esplorare queste bande, poiché la bassa frequenza sarà catturata nei coefficienti di approssimazione della wavelet a ogni livello di decomposizione.

Se vuoi essere sicuro di esplorare frequenze inferiori come Delta e Theta, la decomposizione fino al livello 3 è adeguata, ma dovresti concentrarti sui coefficienti di approssimazione che rappresentano le frequenze più basse.

- Conclusione:
Se il tuo obiettivo è analizzare le frequenze delta e theta (1-8 Hz), il livello 3 di decomposizione è sufficiente, perché stai esaminando una gamma di frequenze fino a 15,625 Hz, che include pienamente le frequenze delta e theta.
Le frequenze molto basse (inferiori a 1 Hz) non saranno catturate dai dati con una DWT 2D su 3 livelli con la risoluzione di campionamento che hai (250 Hz), quindi non è necessario preoccuparsi delle frequenze sotto 1 Hz per i tuoi scopi.

<br>

**IO**

No ti spiego meglio, **quando io ho applicato cliccato la decomposizione uno di 1D, i miei coefficienti erano sufficienti per catturare proprio le specifiche bande di frequenze che mi interessavano:

Questo perché, andando ad esempio ad estrapolare il numero massimo di livelli di decomposizione da questa struttura del mio dato EEG in formato 1D, io **riuscivo ad estrapolarmi proprio i coefficienti di approssimazione e di dettaglio del quarto e del quinto livello**, nello specifico: 

- i coefficienti di approssimazione del 4° livello, integrava proprio le frequenze delta e theta assieme,
- i coefficienti di approssimazione del 5° livello, integrava proprio le frequenze delta, 
- i coefficienti di dettaglio del 5° livello, integrava proprio le frequenze theta

Questo lo sapevo da quanto si sa in generale sulla DWT cioè:

    "
    The discrete wavelet transform (DWT) analyzes the features of a signal in the time and frequency domains by decomposing it into a number of mutually orthogonal components using a single function called the mother wavelet (Majid Aljalal).

    The procedure of DWT in the decomposition applies consecutive lowpass h(n) and high pass g(n) filters. At the start of decomposition, the lowpass h(n) and high pass g(n) filters are concurrently applied to the input EEG signal and produce the corresponding outputs, which are referred to as approximation coefficients and detailed coefficients. 

    According to the sampling theorem, the highest frequency of the signal is fs/2. Using the Mallat algorithm, if the signal is decomposed by L-order, the whole frequency band of the signal is decomposed into L+1 sub-band, that is, [0,𝑓_𝑠/2^(𝐿+1) ] [𝑓_𝑠/2^(𝐿+1) ,𝑓_𝑠/2^𝐿 ]…[𝑓_𝑠/2^2 ,𝑓_𝑠/2] (Na Ji et al.)
    "

Per questo motivo, **ti chiedevo che argomento corretto va passato a "dwtn_max_level" quando io, partendo da dei dati EEG 3D, io prendevo SOLO l'ultima dimensione** 

(come scritto in pywavelets vedi qui https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html) per definire il massimo livello di decomposizioni per un dato 1D ..

Che nel caso 1D c'è scritto che sia: 

    Maximum decomposition level - dwt_max_level, dwtn_max_level
    pywt.dwt_max_level(data_len, filter_len)
    Compute the maximum useful level of decomposition

    Parameters:
    data_len (int) Input data length.

    filter_len (int, str or Wavelet)
    The wavelet filter length. 
    Alternatively, the name of a discrete wavelet or a Wavelet object can be specified.

    Returns: max_level int Maximum level.


Ma poi c'è un'altra funzione che parla di "**n-dimensional data**", ossia questa qui (che è praticamente uguale)

    pywt.dwtn_max_level(shape, wavelet, axes=None)
    Compute the maximum level of decomposition for n-dimensional data.

    This returns the maximum number of levels of decomposition suitable for use with wavedec, wavedec2 or wavedecn.

    Parameters: shape, sequence of ints
    Input data shape.

    wavelet
    Wavelet object or name string, or tuple of wavelets
    Wavelet to use. This can also be a tuple containing a wavelet to apply along each axis in axes.

    axes
    sequence of ints, optional
    Axes over which to compute the DWT. Axes may not be repeated.

    Returns: level int Maximum level.

    **Notes**
    The level returned is the smallest dwt_max_level over all axes


Però c'è anche scritto in quest'ultima:

"**axes: sequence of ints, optional Axes over which to compute the DWT. Axes may not be repeated**."

Ora, **per il caso 2D, che cosa si intende per Axes**?

Perché **non so se mettere allora solo (-1,)**, che sarebbe l'ultimo della mia matrice 3D (e quindi presumo quello dei dati temporali ossia 300) o entrambe le dimensioni della mia matrice 2D che mi aspetto di dare in input alla mia pywavelets.wavedec2 successivamente...


**CHAT**

Grazie per la spiegazione dettagliata! Ora ho capito meglio la tua domanda, e ti aiuto a chiarire il punto.

Quando usi **la DWT 2D con pywt.dwtn_max_level, **DEVI DECIDERE SU QUALI ASSI applicare la decomposizione wavelet**! 
E questo, è legato alla struttura dei tuoi dati (3D nel tuo caso). 

Qui ti spiego i concetti chiave:

**1. Cosa significa "axes" in dwtn_max_level?**

Nel caso della decomposizione 2D (DWT 2D), la funzione dwtn_max_level accetta un **parametro** chiamato "**axes**", che indica su quali dimensioni (assi) della matrice multidimensionale applicare la trasformazione wavelet.

Per i tuoi dati EEG, che sono 3D (ad esempio, con dimensioni [soggetti, canali, tempo] o qualcosa del genere), l'ultima dimensione corrisponde al tempo (in questo caso, 300 campioni). Quando vuoi eseguire una DWT 2D, la decomposizione avviene sui dati spaziali (cioè, canali o altre dimensioni spaziali) e temporali (la dimensione del tempo).

In pywt.dwtn_max_level, il parametro axes **specifica su quali dimensioni applicare la DWT**. 

- Se hai 2D su tempo e canali, vorresti specificare che vuoi applicare la DWT 1) sia sui canali che 2) sul tempo, il che sarebbe rappresentato con axes=(0, 1) (se 0 è la dimensione dei canali e 1 è la dimensione del tempo).

**2. Quando usare (-1,) o (0,1)?**

- **Se** la tua matrice 3D ha [soggetti, canali, tempo] come forma, e **desideri eseguire una DWT 2D SOLO sul tempo**, dovresti specificare solo l'asse del tempo (l'ultimo asse) come argomento di axes. 
- Quindi il parametro dovrebbe essere axes=(-1,), che applica la decomposizione lungo la dimensione temporale.
- **Se** vuoi eseguire una **DWT 2D che coinvolge sia il tempo che i canali**, dovresti passare entrambi gli assi (ad esempio, axes=(0, 1) per canali e tempo).

**3. Esempio pratico**:

Immagina di avere un dato EEG 3D con dimensione [soggetti, canali, tempo] = (N, C, T), dove:

- N è il numero di soggetti,
- C è il numero di canali,
- T è il numero di campioni temporali (300 nel tuo caso).

  - Quando fai una **DWT 1D**, la decomposizione avviene solo sull'asse temporale, quindi passavi solo la dimensione temporale (300 punti) alla funzione dwtn_max_level.
  - Per la **DWT 2D**, 
  
    - Se desideri applicare la decomposizione **su entrambe le dimensioni spaziali e temporali** (e questo applica la DWT su canali e tempo (assumendo che i canali siano la dimensione 1 e il tempo sia la dimensione 2).) userai:

            max_level = pywt.dwtn_max_level(shape=(N, C, T), wavelet='db4', axes=(1, 2))
        
    - Se invece vuoi applicare la DWT **solo sul tempo** (ad esempio, mantenendo invariati i canali), utilizzerai:


            max_level = pywt.dwtn_max_level(shape=(N, C, T), wavelet='db4', axes=(-1,))

Questo applicherà la decomposizione solo sulla dimensione temporale (300 punti).


**4. Conclusione**:

- **axes=(-1,)**: decomposizione solo lungo l'asse temporale (adatto quando vuoi esplorare solo la componente temporale).

- **axes=(0, 1)**: decomposizione su tempo e canali (adatto quando vuoi eseguire una DWT 2D vera e propria).

In base a quello che desideri analizzare, puoi scegliere l'asse giusto: 

Se stai cercando di esplorare frequenze delta e theta (1-8 Hz), e hai trovato che la decomposizione 1D sui dati temporali era sufficiente per analizzare i coefficienti, potresti continuare a usare axes=(-1,). Ma se desideri esplorare tutte le dimensioni spaziali (ad esempio, canali e tempo), axes=(0, 1) è la scelta giusta.


<br>

**IO**

Ok, ma quindi è corretto fare allora un DWT 2D usando come asso solo quello del tempo, ossia (-1, ) e quindi quello dei campioni temporali EEG? 

Ps: la mia matrice di partenza ha (num_trials, num_channels, num_samples)


**CHAT**

Sì, **è corretto fare una DWT 2D utilizzando solo l'asse temporale (ovvero (-1,)) se il tuo obiettivo è applicare la decomposizione wavelet solo sui dati temporali**. 
Questo significa che la decomposizione avverrà solo sulla dimensione del tempo (i tuoi 300 campioni EEG), mentre i canali e i trial rimarranno invariati.

Nel tuo caso, dove la matrice di partenza ha la forma (num_trials, num_channels, num_samples), applicare la decomposizione wavelet solo sull'asse temporale (l'ultima dimensione) è una scelta perfettamente valida, specialmente se stai cercando di analizzare le frequenze specifiche del tempo (come le frequenze delta e theta) nei tuoi segnali EEG.

- Esempio pratico con pywt.dwtn_max_level:

Se la tua matrice ha la forma (num_trials, num_channels, num_samples) (con num_samples = 300), **puoi calcolare il livello massimo di decomposizione usando solo la dimensione temporale** come segue:

    import pywt

    # Forma della matrice (numero di trial, numero di canali, numero di campioni temporali)
    shape = (num_trials, num_channels, num_samples)

    # Calcolare il massimo livello di decomposizione sul solo asse temporale (l'ultimo asse)
    max_level = pywt.dwtn_max_level(shape=shape, wavelet='db4', axes=(-1,))
    print("Massimo livello di decomposizione:", max_level)


<br>

**Cosa succede in questo caso?**

- **axes=(-1,)**: Questo specifica che la decomposizione wavelet viene applicata solo sull'asse del tempo (l'ultimo asse della tua matrice). Quindi i coefficienti di dettaglio e di approssimazione vengono calcolati solo lungo la dimensione temporale, mantenendo invariati i dati per i trial e canali.

- **Decomposizione sui dati temporali**: Applicando la DWT solo sull'asse del tempo, avrai accesso alle bande di frequenza corrispondenti al livello massimo che puoi ottenere con la tua matrice e il filtro wavelet scelto.

**Quindi, per il tuo caso specifico**:
Se l'obiettivo è esplorare le frequenze delta (1-4 Hz) e theta (4-8 Hz), e questi sono associati ai coefficienti di approssimazione e dettaglio della DWT, fare la decomposizione solo lungo l'asse temporale è appropriato, dato che le bande di frequenza di interesse si trovano in quella direzione.

Inoltre, con pywt.dwtn_max_level usando axes=(-1,), la funzione restituirà il massimo livello di decomposizione in base alla lunghezza della dimensione temporale (300 campioni), quindi ti permette di determinare fino a quale livello puoi scomporre i dati temporali mantenendo significativi i coefficienti di onda.

**In sintesi**:

- Se vuoi eseguire **la DWT 2D** sui tuoi dati EEG, ma **solo sulla dimensione temporale** (i campioni EEG), allora axes=(-1,) è la scelta giusta. La DWT verrà applicata solo sui dati temporali, lasciando intatti i dati sui canali e i trial.


#### Implementation of **2D Discrete Wavelet Transform**

#### **All experimental conditions** for all levels of decompositions

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('therapists_data.pkl', 'rb') as f:
    therapists_data = pickle.load(f)

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('patients_data.pkl', 'rb') as f:
    patients_data = pickle.load(f)

In [ ]:
''' PROVA 19/11/2024 POMERIGGIO - CALCOLO DI MEDIA GLOBALE e DEVIAZIONE STANDARD & LABELS - ALL SUBJECTS TH -2D-DWT


Vedere meglio questo aspetto del parametro "mode" per il signal extension mode:

- https://pywavelets.readthedocs.io/en/latest/ref/signal-extension-modes.html#ref-modes

Vedi anche
- https://pywavelets.readthedocs.io/en/latest/ref/2d-dwt-and-idwt.html#pywt.waverec2
-https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html


PS: 

ho messo il mode 'sym' sia a wavedec2d che a waverec2d, come richiesto qui

https://pywavelets.readthedocs.io/en/latest/ref/signal-extension-modes.html#ref-modes

(e che ho pensato si intendesse da applicare con qualsiasi mode, basta che venga inserito sia a 
"wavedec2d" che a "waverec2d")

"periodization - periodization - is like periodic-padding but gives the smallest possible number of decomposition coefficients. IDWT must be performed with the same mode"

ed ora il warning infatti non c'è più

'''

import numpy as np
import pywt

# Calcola il livello massimo di decomposizione
#https://pywavelets.readthedocs.io/en/latest/ref/dwt-discrete-wavelet-transform.html

max_decomposition_level = pywt.dwtn_max_level((300,), 'db4', axes=(-1,))
level = max_decomposition_level  # Livello di decomposizione della wavelet
wavelet = 'db4'  # Tipo di wavelet da utilizzare

def compute_coefficients_per_level_2D(signal_2D, wavelet, max_level):
    
    all_coeffs = []
    for l in range(1, max_level + 1):
        coeffs = pywt.wavedec2(signal_2D, wavelet, mode = 'sym', level=l)
        all_coeffs.append(coeffs)
    return all_coeffs

def discrete_wavelet_2D(EEG_data, level, wavelet, subject_idx):
   
    num_trials, num_channels, num_samples = EEG_data.shape
    
    lev_check = int(np.floor(np.log2(min(num_channels, num_samples))))  # Calcolo massimo livello permesso
    if level > lev_check:
        print(f"Max level of decomposition was exceeded!")
    else:
        print(f"\033[1mMax Level of decomposition\033[0m corresponds to the one calculated, which is \033[1m{level}\033[0m\n\n")
    
    C = np.empty((num_trials, level), dtype = object)
    L = np.empty((num_trials, level), dtype = object)

    # Prepariamo array per i coefficienti ricostruiti
    D = np.zeros((num_trials, num_channels, num_samples, level))  # Dettaglio
    A = np.zeros((num_trials, num_channels, num_samples, level))  # Approssimazione
    
   
    # Per ogni trial e canale
    for tr in range(num_trials):

        trial_C = []  # Lista per memorizzare i coefficienti per ogni trial
        trial_L = []  # Lista per memorizzare le lunghezze dei coefficienti per ogni trial


        signal_2D = EEG_data[tr, :, :]  # Matrice 2D (num_channels, num_samples)

        #print(f"signal_2D.shape is {signal_2D.shape}")
        #signal_2D.shape is (61, 300)

        coeffs_all_levels = compute_coefficients_per_level_2D(signal_2D, wavelet, level)
            
        for l, coeffs in enumerate(coeffs_all_levels):

            current_level = l + 1  # Definisci current_level come l'indice + 1 per accedere ai coefficienti

            # Gestisci separatamente la forma della matrice di approssimazione e dei dettagli
            approx_shape = coeffs[0].shape  # Forma della matrice di approssimazione
            detail_shapes = [detail.shape for detail in coeffs[1]]  # Forme dei dettagli
            
            trial_C.append(coeffs)
            trial_L.append((approx_shape, detail_shapes))  # Salva entrambe le forme


            #+++++++++++++++++++++++++++++++++++++ DETAIL  +++++++++++++++++++++++++++++++++++++
            
            # Ricostruzione del segnale con SOLO i coefficienti di DETTAGLIO per il livello l

            details_to_use = [np.zeros_like(coeffs[0])] + [
            tuple(np.zeros_like(sub_coeff) for sub_coeff in detail_tuple)  # Azzeriamo i dettagli per tutti i livelli
            if l == current_level else detail_tuple  # Manteniamo i dettagli per il livello corrente
            for l, detail_tuple in enumerate(coeffs[1:], start=1)  # Partiamo da l=1 perché coeffs[0] è l'approssimazione
            ]

            reconstructed_detail = pywt.waverec2(details_to_use, wavelet, mode = 'sym')

            #if reconstructed_detail.shape != signal_2D.shape:
                #print(f"Original EEG Data Matrix shape: {signal_2D.shape}, Reconstructed Matrix D shape: {D[tr, :, :, l].shape}")
                #D[tr, :, :, l] = reconstructed_detail
            #else:
            #    print(f"Warning: Dimension mismatch for D at trial {tr}, level {l}: {D[tr, :, :, l].shape} vs {signal_2D.shape}")


            #+++++++++++++++++++++++++++++++++++++ APPROX  +++++++++++++++++++++++++++++++++++++

            # Ricostruzione del segnale con SOLO i coefficienti di APPROSSIMAZIONE per il livello l

            approx_to_use = [coeffs[0]]

            reconstructed_approx = pywt.waverec2(approx_to_use, wavelet, mode = 'sym')

            #if reconstructed_approx.shape != signal_2D.shape:
            #    print(f"Original EEG Data Matrix shape: {signal_2D.shape}, Reconstructed Matrix D shape: {A[tr, :, :, l].shape}")
                #A[tr, :, :, l] = reconstructed_approx
            #else:
            #    print(f"Warning: Dimension mismatch for A at trial {tr}, level {l}: {A[tr, :, :, l].shape} vs {signal_2D.shape}")


        C[tr] = trial_C  # Modifica: Salviamo i coefficienti per ciascun livello
        L[tr] = trial_L  # Modifica: Salviamo i livelli di decomposizione

    wave_subj_name = f'wave_subj_{subject_idx}'

    wave_subj = {
        'C': C,
        'L': L,
        'D': D,
        'A': A,
    }

    return wave_subj_name, wave_subj


def process_all_subjects_2D(therapists_data, level, wavelet):
   
    # Dizionario per memorizzare i risultati separati per condizione sperimentale
    condition_results = {}

    for idx, data_dict in enumerate(therapists_data):
        print(f"\n\n\t\t\t\t\t\033[1mProcessing Subject {idx + 1}\033[0m:\n")

        for condition, value in data_dict.items():
            if '_labels' in condition:
                base_condition = condition.replace('_labels', '') # Rimuove '_labels'
                condition_key = base_condition
                labels_key = condition
            else:
                base_condition = condition
                condition_key = base_condition
                labels_key = f'{base_condition}_labels'
            
            # Modifica: Aggiungi chiavi inizializzate per nuove condizioni
            if '_labels' not in condition and condition_key not in condition_results:
                condition_results[condition_key] = {'D': [], 'A': [], 'A_labels': []}
            
            # Applicazione wavelet solo per array np.ndarray
            if isinstance(value, np.ndarray):
                print(f"\nApplicazione Wavelet 2D per '\033[1m{condition_key}\033[0m'\n")
                print(f"\033[1mShape\033[0m dei dati per \033[1m{condition_key}\033[0m: {value.shape}")

                wave_subj_name, wave_subj = discrete_wavelet_2D(value, level, wavelet, idx + 1)
                
                # Modifica: Aggiungi dati 2D al dizionario
                condition_results[condition_key]['D'].append(wave_subj['D'])
                condition_results[condition_key]['A'].append(wave_subj['A'])
                
                # Gestione etichette
                if labels_key in data_dict:
                    num_labels = data_dict[labels_key]
                    if condition_key in condition_results:
                        print(f"\nFound labels for condition \033[1m{labels_key}\033[0m, length: \033[1m{len(num_labels)}\033[0m\n")
                        condition_results[condition_key]['A_labels'].extend(num_labels)
            else:
                print(f"\033[1m{labels_key}\033[0m' non è un np.array, non applicare la wavelet")
    
    # Preparazione risultati concatenati
    all_subjects_condition_results = {}

    for condition_key, results in condition_results.items():
        if "_labels" in condition_key or not results['D'] or not results['A']:
            print(f"\nSkipping \033[1m{labels_key}\033[0m as it is a label or has no valid data.")
            continue

        wave_condition_name = f'wave_{condition_key}'
        print(f"\n\nResults for \t\t\t\t\t\033[1m{wave_condition_name}\033[0m:\n\n")

        D_concatenated = np.concatenate(results['D'], axis=0)
        A_concatenated = np.concatenate(results['A'], axis=0)

        Dm = np.mean(D_concatenated, axis=0)
        Am = np.mean(A_concatenated, axis=0)
        D_std = np.std(D_concatenated, axis=0)
        A_std = np.std(A_concatenated, axis=0)

        wave_condition = {
            'D': D_concatenated,
            'A': A_concatenated,
            'Dm': Dm,
            'Am': Am,
            'D_std': D_std,
            'A_std': A_std,
            'A_labels': results['A_labels']
        }
        
        print(f"\n\nResults for \033[1m{wave_condition_name}\033[0m:")
        print(f"D shape before mean for the condition \033[1m'{condition_key}'\033[0m: {D_concatenated.shape}")
        print(f"A shape before mean for the condition \033[1m'{condition_key}'\033[0m: {A_concatenated.shape}")
        print(f"Dm shape for condition \033[1m'{condition_key}'\033[0m after mean: {Dm.shape}")
        print(f"Am shape for condition \033[1m'{condition_key}'\033[0m after mean: {Am.shape}")
        print(f"D_std shape for condition \033[1m'{condition_key}'\033[0m after std: {D_std.shape}")
        print(f"A_std shape for condition \033[1m'{condition_key}'\033[0m after std: {A_std.shape}")

        print(f"D_concatenated shape: {D_concatenated.shape}, A_concatenated shape: {A_concatenated.shape}")
        all_subjects_condition_results[wave_condition_name] = wave_condition

    return all_subjects_condition_results

In [ ]:
# Richiamo della funzione per processare tutti i soggetti e ottenere i risultati per ciascuna condizione
all_subjects_condition_results_th = process_all_subjects_2D(therapists_data, level, wavelet)

In [ ]:

#len(patients_data) 
#output : 15

#patients_data[0].keys()
#output : dict_keys(['baseline_1', 'vision_resp_1', 
                    #'th_resp_1', 'shared_resp_1', 
                    #'baseline_1_labels', 'vision_resp_1_labels',
                    #'th_resp_1_labels', 'shared_resp_1_labels'])

#patients_data[0].keys()

In [ ]:
all_subjects_condition_results_pt = process_all_subjects_2D(patients_data, level, wavelet)

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
!pwd

In [ ]:
#Salvo ricostruzioni 4° e 5° livello terapisti

''' PATH  --> cd Plots_Sliding_Estimator_MNE '''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('all_subjects_condition_results_th.pkl', 'wb') as f:
#    pickle.dump(all_subjects_condition_results_th, f)
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_subjects_condition_results_th_2D.pkl', 'wb') as f:
    pickle.dump(all_subjects_condition_results_th, f)

In [ ]:
#Salvo ricostruzioni 4° e 5° livello pazienti

''' PATH  --> cd Plots_Sliding_Estimator_MNE'''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('new_all_subjects_condition_results_pt.pkl', 'wb') as f:
#    pickle.dump(all_subjects_condition_results_pt, f)
    
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_subjects_condition_results_pt_2D.pkl', 'wb') as f:
    pickle.dump(all_subjects_condition_results_pt, f)

### STEP 4.3.2.3.1 - All Therapists EEG Data Reconstructions (2-DWT)

#### Concatenazione All Single Subject Data (TH) per tutte le condizioni sperimentali, per ogni livello di ricostruzione (θ+δ, θ and δ)

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''

#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('all_subjects_condition_results_th.pkl', 'rb') as f:
#    all_subjects_condition_results_th = pickle.load(f)
    
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle


# Caricare l'intero dizionario annidato con pickle
with open('new_all_subjects_condition_results_th_2D.pkl', 'rb') as f:
    new_all_subjects_condition_results_th_2D = pickle.load(f)

In [ ]:
new_all_subjects_condition_results_th_2D.keys()

In [ ]:
#print(f"\033[1mChiavi di primo ordine\033[0m i.e., all_subjects_condition_results_th: \n\n{all_subjects_condition_results_th.keys()}")
#print(f"\n\n\033[1mChiavi di ogni condizione sperimentale\033[0m, i.e., 'wave_baseline_1': {all_subjects_condition_results_th['wave_baseline_1'].keys()}")

#all_subjects_condition_results['wave_baseline_1'].keys()


print(f"\033[1mChiavi di primo ordine\033[0m i.e., new_all_subjects_condition_results_th_2D: \n\n{new_all_subjects_condition_results_th_2D.keys()}")
print(f"\n\n\033[1mChiavi di ogni condizione sperimentale\033[0m, i.e., 'wave_baseline_1': {new_all_subjects_condition_results_th_2D['wave_baseline_1'].keys()}")


In [ ]:
#new_all_subjects_condition_results_th['wave_baseline_1'].keys()
print(new_all_subjects_condition_results_th_2D['wave_baseline_1']['A'].shape)
print(new_all_subjects_condition_results_th_2D['wave_baseline_1']['D'].shape)

In [ ]:
'''
Da "all_subjects_condition_results" ottengo:

Le ricostruzioni 4° e 5° livello di tutti i terapisti per tutte le condizioni sperimentali dai coefficienti di approssimazione
Le ricostruzioni 5° livello di tutti i terapisti per tutte le condizioni sperimentali dai coefficienti di dettaglio

				(i.e., single_th_all_extracted_reconstructions):

'''

import numpy as np

# Definizione degli indici dei canali desiderati
selected_channels = [12, 30, 48]  # Indici per Fz, Cz, Pz

# Creazione di un dizionario dei dati di tutti i terapisti singolarmente, per salvare le ricostruzioni estratte per livello 4 e 5
#single_th_all_extracted_reconstructions = {}

new_single_th_all_extracted_reconstructions_2D = {}

# Iterazione su tutte le condizioni sperimentali di tutti i soggetti 

#'OLD VERSION'
#for condition, data in all_subjects_condition_results_th.items():

for condition, data in new_all_subjects_condition_results_th_2D.items():
    
    # Estrarre le etichette per questa condizione
    A_labels = data['A_labels']
    
    # Estrazione della matrice 'A' per le ricostruzioni del segnale con coefficienti di approssimazione
    A = data['A']
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Estrazione della matrice 'D' per le ricostruzioni del segnale con coefficienti di approssimazione
    D = data['D']
    
    # Estrarre solo i canali selezionati e i livelli di ricostruzione desiderati (4° e 5°, quindi indice -2 e -1)
    theta_reconstruction = A[:, selected_channels, :, -2]  # 4° livello di ricostruzione
    delta_reconstruction = A[:, selected_channels, :, -1]  # 5° livello di ricostruzione
    
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Ottenere i coefficienti di dettaglio del 5° livello di ricostruzione (theta range)
    coeff_fifth_detail_theta = D[:, selected_channels, :, -1]  # Coefficienti di dettaglio del livello 5
    
    
    # Trasponi per ottenere la forma desiderata: (trials, canali, punti temporali)
    theta_reconstruction = theta_reconstruction.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    delta_reconstruction = delta_reconstruction.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    coeff_fifth_detail_theta = coeff_fifth_detail_theta.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Creare un sotto-dizionario per organizzare 
    #le ricostruzioni EEG del livello 4 'theta' e livello 5 'delta' dai coeff di approx
    #le ricostruzioni EEG del livello 4 'theta' e livello 5 'delta' dai coeff di detail
    
    new_single_th_all_extracted_reconstructions_2D[condition] = {
        'theta': theta_reconstruction,
        'delta': delta_reconstruction,
        'coeff_fifth_detail_theta': coeff_fifth_detail_theta, 
        'labels': A_labels
    }

# Verifica delle dimensioni del risultato estratto per una condizione specifica
print(f"\t\t\033[1mRicostruzioni 4° e 5° livello di tutti i terapisti per tutte le condizioni sperimentali")
#print(f"\n\n\t\t\t\t(i.e., \033[1msingle_th_all_extracted_reconstructions\033[0m):\n")

print(f"\n\n\t\t\t\t(i.e., \033[1mnew_single_th_all_extracted_reconstructions_2D\033[0m):\n")


#for condition, extracted_data in single_th_all_extracted_reconstructions.items():

#'''AGGIUNTI COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''

for condition, extracted_data in new_single_th_all_extracted_reconstructions_2D.items():
    
    print(f"Condizione: \033[1m{condition}\033[0m, "
          f"Theta shape: \033[1m{extracted_data['theta'].shape}\033[0m, "
          f"Delta shape: \033[1m{extracted_data['delta'].shape}\033[0m, "
          f"Coeff Fifth Detail shape: \033[1m{extracted_data['coeff_fifth_detail_theta'].shape}\033[0m, "
          f"Labels: \033[1m{len(extracted_data['labels'])}\033[0m")

# STEP 2: Concatenare i dati e le etichette di tutti i soggetti per i livelli di ricostruzione 4 e 5

# Inizializzazione delle liste per raccogliere i dati e le etichette del 4° e 5° livello di ricostruzione da coeff approx

all_th_fourth = []
labels_th_fourth = []
exp_conditions_fourth = []

all_th_fifth = []
labels_th_fifth = []
exp_conditions_fifth = []


#'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''

all_th_fifth_detail = []
labels_th_fifth_detail = []
exp_conditions_fifth_detail = []

# Iterazione su tutte le condizioni sperimentali

#for condition, data in single_th_all_extracted_reconstructions.items():
for condition, data in new_single_th_all_extracted_reconstructions_2D.items():    
    
    # Preparazione delle liste per dati e etichette per ogni condizione
    dati_fourth = [None] * 4  # Per 'baseline', 'th_resp', 'vision_resp', 'shared_resp'
    labels_fourth = [None] * 4
    
    dati_fifth = [None] * 4
    labels_fifth = [None] * 4
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    dati_fifth_detail = [None] * 4
    labels_fifth_detail = [None] * 4
    
    for chiave, valore in data.items():
        
        if chiave == 'theta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            if 'baseline' in condition:
                dati_fourth[0] = valore
                labels_fourth[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fourth[1] = valore
                labels_fourth[1] = data['labels']
            
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fourth[2] = valore
                labels_fourth[2] = data['labels']
                
            elif 'shared_resp' in condition:
                dati_fourth[3] = valore
                labels_fourth[3] = data['labels']
                
        elif chiave == 'delta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            if 'baseline' in condition:
                dati_fifth[0] = valore
                labels_fifth[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fifth[1] = valore
                labels_fifth[1] = data['labels']
            
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fifth[2] = valore
                labels_fifth[2] = data['labels']
                
                
            elif 'shared_resp' in condition:
                dati_fifth[3] = valore
                labels_fifth[3] = data['labels']
        
        elif chiave == 'coeff_fifth_detail_theta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            
            if 'baseline' in condition:
                dati_fifth_detail[0] = valore
                labels_fifth_detail[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fifth_detail[1] = valore
                labels_fifth_detail[1] = data['labels']
                
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fifth_detail[2] = valore
                labels_fifth_detail[2] = data['labels']
                
            elif 'shared_resp' in condition:
                dati_fifth_detail[3] = valore
                labels_fifth_detail[3] = data['labels']
                
            
    # Filtrare i valori non None
    dati_fourth = [d for d in dati_fourth if d is not None]
    labels_fourth = [l for l in labels_fourth if l is not None]
    
    dati_fifth = [d for d in dati_fifth if d is not None]
    labels_fifth = [l for l in labels_fifth if l is not None]
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    dati_fifth_detail = [d for d in dati_fifth_detail if d is not None]
    labels_fifth_detail = [l for l in labels_fifth_detail if l is not None]
    
    # Concatenare i dati e le etichette
    if dati_fourth:
        datas_fourth = np.concatenate(dati_fourth, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fourth = np.concatenate([np.array(l) for l in labels_fourth], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_th_fourth.append(datas_fourth)
        labels_th_fourth.append(labels_fourth)
        exp_conditions_fourth.append(condition)
    
    if dati_fifth:
        datas_fifth = np.concatenate(dati_fifth, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fifth = np.concatenate([np.array(l) for l in labels_fifth], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_th_fifth.append(datas_fifth)
        labels_th_fifth.append(labels_fifth)
        exp_conditions_fifth.append(condition)
    
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    if dati_fifth_detail:
        
        datas_fifth_detail = np.concatenate(dati_fifth_detail, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fifth_detail = np.concatenate([np.array(l) for l in labels_fifth_detail], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_th_fifth_detail.append(datas_fifth_detail)
        labels_th_fifth_detail.append(labels_fifth_detail)
        exp_conditions_fifth_detail.append(condition)

# STEP 3: Concatenazione finale di tutti i dati e le etichette

# Concatenazione finale di tutti i dati e le etichette

#'''PER COEFFICIENTI DI APPROSSIMAZIONE 4° LIVELLO (i.e., range 0-7.812Hz)'''
if all_th_fourth:
    all_fourth = np.concatenate(all_th_fourth, axis=0)
else:
    all_fourth = np.array([])

if labels_th_fourth:
    all_fourth_labels = np.concatenate(labels_th_fourth, axis=0)
else:
    all_fourth_labels = np.array([])

    
#'''PER COEFFICIENTI DI APPROSSIMAZIONE 5° LIVELLO (i.e., range 0-3.9Hz)'''    
if all_th_fifth:
    all_fifth = np.concatenate(all_th_fifth, axis=0)
else:
    all_fifth = np.array([])

if labels_th_fifth:
    all_fifth_labels = np.concatenate(labels_th_fifth, axis=0)
else:
    all_fifth_labels = np.array([])
    

#'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
if all_th_fifth_detail:
    all_fifth_detail = np.concatenate(all_th_fifth_detail, axis=0)
else:
    all_fifth_detail = np.array([])

if labels_th_fifth_detail:
    all_fifth_detail_labels = np.concatenate(labels_th_fifth_detail, axis=0)
else:
    all_fifth_detail_labels = np.array([])
    

# Verifica delle dimensioni del risultato finale
print(f"\n\n\n\t\tTUTTI I TRIAL DI TUTTI I SOGGETTI DI OGNI CONDIZIONE SPERIMENTALE - PER LIVELLO DI RICOSTRUZIONE ")

print(f"\n\033[1m4° livello\033[0m di ricostruzione da Coeff di Approx - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fourth\033[0m: \033[1m{all_fourth.shape}\033[0m, Length di \033[1mall_fourth_labels\033[0m: \033[1m{len(all_fourth_labels)}\033[0m")

print(f"\n\033[1m5° livello\033[0m di ricostruzione da Coeff di Approx - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fifth\033[0m: \033[1m{all_fifth.shape}\033[0m, Length di \033[1mall_fifth_labels\033[0m: \033[1m{len(all_fifth_labels)}\033[0m")

print(f"\n\033[1m5° livello\033[0m di ricostruzione da Coeff di Detail - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fifth_detail\033[0m: \033[1m{all_fifth_detail.shape}\033[0m, Length di \033[1mall_fifth_detail_labels\033[0m: \033[1m{len(all_fifth_detail_labels)}\033[0m")


In [ ]:
!pwd

In [ ]:
#Salvo ricostruzioni 4° e 5° livello per singolo terapista con concatenazioni dati e labels 

''' PATH  --> cd Plots_Sliding_Estimator_MNE '''

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('single_th_all_extracted_reconstructions.pkl', 'wb') as f:
#    pickle.dump(single_th_all_extracted_reconstructions, f)
    
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''

import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_single_th_all_extracted_reconstructions_2D.pkl', 'wb') as f:
    pickle.dump(new_single_th_all_extracted_reconstructions_2D, f)


In [ ]:
'''SALVO IN UN GRANDE DIZIONARIO I DATI E LE LABELS CONCATENATI DI TUTTI I SOGGETTI PER IL LIVELLO DI RICOSTRUZIONE'''


#Creo dizionario per le concatenazioni di dati e labels a seconda del livello di ricostruzione del segnale EEG 
new_all_th_concat_reconstructions_2D = {'all_th_fourth': all_fourth, 
                                 'all_th_fourth_labels': all_fourth_labels,
                                 'all_th_fifth': all_fifth,
                                 'all_th_fifth_labels': all_fifth_labels,
                                 'all_th_fifth_detail': all_fifth_detail,
                                 'all_th_fifth_detail_labels': all_fifth_detail_labels
                                }

'''STAMPA DELLE CHIAVI e SHAPE'''
#all_th_concat_reconstructions.keys()
#all_th_concat_reconstructions['all_th_fourth'].shape
#all_th_concat_reconstructions['all_th_fourth_labels'].shape

#all_th_concat_reconstructions['all_th_fifth'].shape
#all_th_concat_reconstructions['all_th_fifth_labels'].shape



#all_th_concat_theta = {'all_th_fourth': all_fourth, 
#                       'all_th_fourth_labels': all_fourth_labels}


#all_th_concat_delta = {'all_th_fifth': all_fifth,
#                       'all_th_fifth_labels': all_fifth_labels}


#all_th_concat_theta.keys()
#all_th_concat_delta.keys()

In [ ]:
new_all_th_concat_reconstructions_2D.keys()

In [ ]:
!pwd

In [ ]:
'''SALVO I DATI CONCATENATI DI TUTTI I SOGGETTI TERAPISTI, RISPETTO AD UNO SPECIFICO LIVELLO DI RICOSTRUZIONE

import pickle
# Salvare l'intero dizionario annidato con pickle
with open('all_fourth_th_2D.pkl', 'wb') as f:
    pickle.dump(all_fourth, f) 


import pickle
# Salvare l'intero dizionario annidato con pickle
with open('all_fifth_th_2D.pkl', 'wb') as f:
    pickle.dump(all_fifth, f) 

    
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_fifth_detail_th_2D.pkl', 'wb') as f:
    pickle.dump(all_fifth_detail, f) 
'''

#SALVO I DATI CONCATENATI DI TUTTI I SOGGETTI TERAPISTI, RISPETTO AD OGNI LIVELLO DI RICOSTRUZIONE INSIEME
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_th_concat_reconstructions_2D.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_2D, f)   
    


In [ ]:
#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_single_th_all_extracted_reconstructions.pkl', 'rb') as f:
#    new_single_th_all_extracted_reconstructions = pickle.load(f)

In [ ]:
#Dizionario con dati e labels 
#a seconda del livello di ricostruzione del segnale EEG 
#di ogni singolo soggetto 
#per tutte le condizioni sperimentali SEPARATAMENTE!

'''OLD'''
#print(f"\n\033[1msingle_th_all_extracted_reconstructions.keys()\033[0m: \n{single_th_all_extracted_reconstructions.keys()}\n")
#print(f"\n\033[1msingle_th_all_extracted_reconstructions['wave_baseline_1'].keys()\033[0m: {single_th_all_extracted_reconstructions['wave_baseline_1'].keys()}")


'''NEW'''
print(f"\n\033[1mnew_single_th_all_extracted_reconstructions_2D.keys()\033[0m: \n{new_single_th_all_extracted_reconstructions_2D.keys()}\n")
print(f"\n\033[1mnew_single_th_all_extracted_reconstructions_2D['wave_baseline_1'].keys()\033[0m: {new_single_th_all_extracted_reconstructions_2D['wave_baseline_1'].keys()}")


#single_th_all_extracted_reconstructions['wave_baseline_1']['theta'].shape
#single_th_all_extracted_reconstructions['wave_baseline_1']['delta'].shape
#len(single_th_all_extracted_reconstructions['wave_baseline_1']['labels'])

In [ ]:
# Itera su ogni chiave nel dizionario new_single_th_all_extracted_reconstructions
for main_key in new_single_th_all_extracted_reconstructions_2D.keys():
    
    # Verifica se 'coeff_fifth_detail_theta' è presente tra le sottochiavi
    if 'coeff_fifth_detail_theta' not in new_single_th_all_extracted_reconstructions_2D[main_key]:
        print(f"La chiave '{main_key}' \033[1mNON contiene\033[0m 'coeff_fifth_detail_theta'")
    else:
        print(f"La chiave '{main_key}' contiene 'coeff_fifth_detail_theta'")

In [ ]:
'''
Questa struttura consente di avere i dati correttamente organizzati e concatenati per ogni soggetto 
in base al livello di ricostruzione, 
mantenendo la corrispondenza tra dati e etichette per ogni condizione sperimentale

Da           "single_th_all_extracted_reconstructions_2D"       a            "subject_level_concatenations_th_2D"

Da           "new_single_th_all_extracted_reconstructions_2D"       a       "new_subject_level_concatenations_th_2D"
'''

import numpy as np

# Dizionario per contenere i dati concatenati per ogni soggetto e livello di ricostruzione
new_subject_level_concatenations_th_2D = {}

# Variabile per tracciare il soggetto precedente
previous_subject_suffix = None

print(f"\t\t\033[1mConcatenazione dati 4° e 5° livello di OGNI terapista di TUTTE le condizioni sperimentali INSIEME\033[0m")
#print(f"\n\t\tda\t\033[1m'single_th_all_extracted_reconstructions'\033[0m \ta\t\033[1m'subject_level_concatenations_th'\033[0m")

print(f"\n\tda\t\033[1m'new_single_th_all_extracted_reconstructions_2D'\033[0m \ta\t\033[1m'new_subject_level_concatenations_th_2D'\033[0m")

# Iterazione su tutte le chiavi di single_th_all_extracted_reconstructions

#'''OLD VERSION'''
#for condition, data in single_th_all_extracted_reconstructions.items():

for condition, data in new_single_th_all_extracted_reconstructions_2D.items():
    
    # Estrazione del suffisso numerico del soggetto (es. '1', '2', ...)
    subject_suffix = condition.split('_')[-1]  # Prende solo la parte numerica
    
    # Creazione del nome della chiave del soggetto specifico
    subj_name = f'th_{subject_suffix}'  # Crea la chiave con prefisso 'th_' e suffisso numerico
    
    # Se stiamo per passare a un nuovo soggetto, stampiamo le dimensioni delle concatenazioni per il soggetto precedente
    if previous_subject_suffix is not None and subject_suffix != previous_subject_suffix:
        
        print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('th_{previous_subject_suffix}'):\033[0m\n")
        prev_subject_name = f'th_{previous_subject_suffix}'
        
        #levels = subject_level_concatenations_th[prev_subject_name]
        
        levels = new_subject_level_concatenations_th_2D[prev_subject_name]
        
        # Concatenazione dei dati prima della stampa
        theta_concat = np.concatenate(levels['theta'], axis=0)
        delta_concat = np.concatenate(levels['delta'], axis=0)
        
        #Coefficienti di dettaglio 5° livello theta
        theta_concat_strict = np.concatenate(levels['theta_strict'], axis=0)
        
        labels_concat = np.concatenate(levels['labels'], axis=0)
        
        #if 'coeff_fifth_detail_theta' not in levels:
        #    print(f"La chiave 'coeff_fifth_detail_theta' non è presente per il soggetto: {prev_subject_name}")

        print(f"Soggetto: \033[1m{prev_subject_name}\033[0m, "
              f"Theta shape: \033[1m{np.concatenate(levels['theta'], axis=0).shape}\033[0m, "
              f"Delta shape: \033[1m{np.concatenate(levels['delta'], axis=0).shape}\033[0m, "
              f"Theta Strict shape: \033[1m{np.concatenate(levels['theta_strict'], axis=0).shape}\033[0m, "
              f"Labels length: \033[1m{len(np.concatenate(levels['labels'], axis=0))}\033[0m")
        
        
        #'''OLD'''
        # Salvataggio dei dati concatenati nel dizionario come array NumPy
        #subject_level_concatenations_th[prev_subject_name]['theta'] = theta_concat
        #subject_level_concatenations_th[prev_subject_name]['delta'] = delta_concat
        #subject_level_concatenations_th[prev_subject_name]['labels'] = labels_concat
        
        
        #'''NEW'''
        new_subject_level_concatenations_th_2D[prev_subject_name]['theta'] = theta_concat
        new_subject_level_concatenations_th_2D[prev_subject_name]['delta'] = delta_concat
        
        new_subject_level_concatenations_th_2D[prev_subject_name]['theta_strict'] = theta_concat_strict
        
        new_subject_level_concatenations_th_2D[prev_subject_name]['labels'] = labels_concat
    
    #'''OLD'''
    # Inizializzare il dizionario per il soggetto specifico se non esiste già
    #if subj_name not in subject_level_concatenations_th:
    #    subject_level_concatenations_th[subj_name] = {
    #        'theta': [],
    #        'delta': [],
    #        'labels': []
    #    }
    
    #'''NEW'''
    if subj_name not in new_subject_level_concatenations_th_2D:
        new_subject_level_concatenations_th_2D[subj_name] = {
            'theta': [],
            'delta': [],
            'theta_strict': [],
            'labels': []
        }
        
    # Stampiamo le informazioni per ogni condizione
    print(f"\n\n\nSoggetto: \033[1m{subj_name}\033[0m, Condizione: \033[1m{condition}\033[0m")
    print(f"  - Theta shape: \033[1m{data['theta'].shape}\033[0m")
    print(f"  - Delta shape: \033[1m{data['delta'].shape}\033[0m")
    print(f"  - Theta Strict: \033[1m{data['coeff_fifth_detail_theta'].shape}\033[0m")
    print(f"  - Labels shape: \033[1m{len(data['labels'])}\033[0m")
    print(f"  - Valori unici delle etichette: \033[1m{np.unique(data['labels'])}\033[0m")
    
    
    #'''OLD'''
    # Concatenazione dei dati per i livelli theta, delta e labels
    #subject_level_concatenations_th[subj_name]['theta'].append(data['theta'])
    #subject_level_concatenations_th[subj_name]['delta'].append(data['delta'])
    #subject_level_concatenations_th[subj_name]['labels'].append(data['labels'])
    
    
    #'''NEW'''
    
    # Concatenazione dei dati per i livelli theta, delta e labels
    new_subject_level_concatenations_th_2D[subj_name]['theta'].append(data['theta'])
    new_subject_level_concatenations_th_2D[subj_name]['delta'].append(data['delta'])
    
    new_subject_level_concatenations_th_2D[subj_name]['theta_strict'].append(data['coeff_fifth_detail_theta'])
    
    new_subject_level_concatenations_th_2D[subj_name]['labels'].append(data['labels'])
    
    # Aggiorna il soggetto precedente
    previous_subject_suffix = subject_suffix

# Dopo aver iterato su tutte le condizioni, concatenare e stampare le informazioni dell'ultimo soggetto
if previous_subject_suffix is not None:
    
    last_subject_name = f'th_{previous_subject_suffix}'
    #levels = subject_level_concatenations_th[last_subject_name]
    levels = new_subject_level_concatenations_th_2D[last_subject_name]
    
    print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('{last_subject_name}'):\033[0m\n")
    
    # Concatenazione dei dati dell'ultimo soggetto
    theta_concat = np.concatenate(levels['theta'], axis=0)
    delta_concat = np.concatenate(levels['delta'], axis=0)
    
    theta_concat_strict = np.concatenate(levels['theta_strict'], axis=0)
    
    labels_concat = np.concatenate(levels['labels'], axis=0)
    
    #'''OLD'''
    # Salvataggio dei dati concatenati dell'ultimo soggetto nel dizionario come array NumPy
    #subject_level_concatenations_th[last_subject_name] = {
    #    'theta': theta_concat,
    #    'delta': delta_concat,
    #    'labels': labels_concat
    #}
    
    #'''NEW'''
    # Salvataggio dei dati concatenati dell'ultimo soggetto nel dizionario come array NumPy
    new_subject_level_concatenations_th_2D[last_subject_name] = {
       'theta': theta_concat,
        'delta': delta_concat,
        'theta_strict': theta_concat_strict,
        'labels': labels_concat
    }
    
    
    print(f"Soggetto: \033[1m{last_subject_name}\033[0m, "
          f"Theta shape: \033[1m{np.concatenate(levels['theta'], axis=0).shape}\033[0m, "
          f"Delta shape: \033{np.concatenate(levels['delta'], axis=0).shape}\033[0m, "
          f"Labels length: \033[1m{len(np.concatenate(levels['labels'], axis=0))}\033[0m\n\n")



In [ ]:
'''CHIAVI DI TUTTO IL DIZIONARIO '''
#subject_level_concatenations_th.keys()


new_subject_level_concatenations_th_2D.keys()


#SOGGETTO 1

#CHIAVI
#subject_level_concatenations_th['th_1'].keys()

#DATI
#subject_level_concatenations_th['th_1']['theta'].shape

#new_subject_level_concatenations_th['th_1']['theta'].shape

#subject_level_concatenations_th['th_1']['delta'].shape

#LABELS
#subject_level_concatenations_th['th_1']['labels'].shape)
#type(subject_level_concatenations_th['th_1']['labels'])

# Check della concantenazione delle labels TH_1

#subject_level_concatenations_th['th_1']['labels'][:42]
#subject_level_concatenations_th['th_1']['labels'][41:81]
#subject_level_concatenations_th['th_1']['labels'][81:120]
#subject_level_concatenations_th['th_1']['labels'][121:164]

In [ ]:
#subject_level_concatenations_th['th_15']['labels'].shape

In [ ]:
#subject_level_concatenations_th['th_1'].keys()

new_subject_level_concatenations_th_2D['th_19'].keys()


In [ ]:
#unique_values, counts = np.unique(subject_level_concatenations_th['th_1']['labels'], return_counts=True)

#unique_values, counts = np.unique(new_subject_level_concatenations_th['th_1']['labels'], return_counts=True)

In [ ]:
#unique_values
#counts
#counts[0]

In [ ]:
!pwd

In [ ]:
#Salvo ricostruzioni 4° e 5° livello per singolo terapista con concatenazioni dati e labels 

    
''' PATH  --> cd Plots_Sliding_Estimator_MNE '''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('subject_level_concatenations_pt.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations_pt, f)
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th_2D.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_th_2D, f)


### STEP 4.3.2.3.1.2 - All Therapists EEG Data Reconstructions (**STFT**)

#### **Calcolo Spettrogrammi** All **SINGLE** Subject Data (**TH**) per **Tutte le Condizioni sperimentali**

In [1]:
!pwd

/home/stefano/Interrogait/Analyses_EEG_1_20


In [2]:
cd ..

/home/stefano/Interrogait


In [3]:
cd New_Plots_Sliding_Estimator_MNE_1_45

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [4]:
import numpy

In [5]:
import numpy as np
print(np.__version__)

1.23.5


In [6]:
# Caricare l'intero dizionario annidato con pickle
import pickle

fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{fam_path}therapists_data.pkl', 'rb') as f:
    therapists_data = pickle.load(f)

In [7]:
print(len(therapists_data))
print(therapists_data[0].keys())

20
dict_keys(['baseline_1', 'th_resp_1', 'pt_resp_1', 'shared_resp_1', 'baseline_1_labels', 'th_resp_1_labels', 'pt_resp_1_labels', 'shared_resp_1_labels'])


In [8]:
therapists_data[0]['baseline_1'].shape

(44, 61, 300)

In [ ]:
'''CREAZIONE SPETTROGRAMMI FREQUENZE x TEMPO'''
import numpy as np
import pywt
from scipy.signal import stft

def create_spectograms_from_stft(data, window_size = 50, step_size = 25, fs = 250):
    
    # Dizionario per memorizzare i risultati separati per condizione sperimentale
    condition_results = {}
    
    for idx, data_dict in enumerate(data):
        print(f"\n\n\t\t\t\t\t\033[1mProcessing Subject {idx + 1}\033[0m:\n")

        for condition, value in data_dict.items():
            if '_labels' in condition:
                base_condition = condition.replace('_labels', '')  # Rimuove '_labels'
                condition_key = base_condition
                labels_key = condition
            else:
                base_condition = condition
                condition_key = base_condition
                labels_key = f'{base_condition}_labels'
            
            # Aggiungi chiavi inizializzate per nuove condizioni
            if '_labels' not in condition and condition_key not in condition_results:
                condition_results[condition_key] = {'spectrograms': [], 'labels': []}
            
            # Applicazione wavelet solo per array np.ndarray
            if isinstance(value, np.ndarray):
                print(f"\nApplicazione STFT per '\033[1m{condition_key}\033[0m'\n")
                print(f"\033[1mShape\033[0m dei dati per \033[1m{condition_key}\033[0m: {value.shape}")
                
                
                # Esegui STFT per ogni canale e trial          
                
                #La funzione stft di SciPy restituisce uno spettrogramma con la forma (n_frequencies, n_time_steps),
                #quindi:38 corrisponde al numero di bin di frequenza calcolati a partire dalla finestra FFT di 75 punti.
                
                #Infatti, per una finestra di lunghezza 75, il numero di bin è calcolato (in questo caso, dato che 75 è dispari) come (75 + 1) // 2, ovvero 38.
                #Il numero di passi temporali (n_time_steps) viene invece calcolato in base alla lunghezza del segnale e ai parametri di finestra e overlap.
                
                #Nel tuo caso, estraendo 250 punti (da 50 a 300) con nperseg=75 e noverlap=25 (cioè con un salto di 50 campioni per finestra), 
                #il numero di segmenti dovrebbe essere:
                #1 + [250−75/75-25] = 1 + [175/50]  = 1 + 3 = 4

                #Pertanto, il risultato di stft (cioè Zxx) ha forma (38, 4) e non (4, 38). 
                #Se ti aspetti una struttura con l'asse del tempo come terza dimensione (ad esempio, (trial, canali, tempo, frequenze))
                #potresti dover trasporre l'array in modo da scambiare le dimensioni frequenza e tempo.
                
                '''
                1) crearmi una lista per salvarmi poi tutti gli spettrogrammi di tutti i trials
                2) per il trials corrente mi salvo lo spettrogramma e lo appendo poi ad 1)
                3) converto la lista di tutti gli spettrogrammi di tutti i trials della condizione corrente in array numpy 
                4) carico poi l'array numpy dentro il dizionario della condizione corrente dentro la chiave 'spectrograms'
                '''
                
                all_trial_spectrograms = []

                for trial in range(value.shape[0]):
                    single_trial_spectrograms = []  # Lista per memorizzare gli spettrogrammi per il trial corrente

                    for channel in range(value.shape[1]):
                        
                        single_channel_data = value[trial, channel, 50:300]  # Estrai i dati del singolo canale
                        
                        #print(f"Segment length: {len(single_channel_data)}")
                    
                        '''TIENI A MENTE CHE DUE PARAMETRI GESTISCONO IL PADDING QUI AUTOMATICAMENTE, CHE SONO:
                        
                        boundary='zeros', 
                        padded=True,
                        
                        PER QUESTO MOTIVO LE FINESTRE SARANNO 11 E NON 9.
                        
                        IN QUESTO MODO, SI MIGLIORA LA RISOLUZIONE IN FREQUENZA ALL'INIZIO E FINE DEL SEGNALE (DI 250 PUNTI!)
                        ANDANDO IN QUESTO MODO A RIDURRE GLI EFFETTI DI BORDO
                        '''
                        
                        f, t, Zxx = stft(single_channel_data, fs=fs, window='hann', nperseg=window_size, noverlap=step_size)
                        
                        single_trial_spectrograms.append(Zxx)  # Aggiungi lo spettrogramma calcolato per il canale corrente

                    all_trial_spectrograms.append(np.array(single_trial_spectrograms))  # Forma: (numero_canali, frequenze, tempo)

                condition_results[condition_key]['spectrograms'].extend(all_trial_spectrograms)

                # Gestione etichette
                if labels_key in data_dict:
                    num_labels = data_dict[labels_key]
                    if condition_key in condition_results:
                        print(f"\nFound labels for condition \033[1m{labels_key}\033[0m, length: \033[1m{len(num_labels)}\033[0m\n")
                        condition_results[condition_key]['labels'].extend(num_labels)
            else:
                print(f"\033[1m{labels_key}\033[0m' non è un np.array, non applicare la STFT ")
    
    # Preparazione risultati concatenati
    all_subjects_condition_results = {}

    for condition_key, results in condition_results.items():
        if "_labels" in condition_key or len(results['spectrograms']) == 0:  # Verifica che ci siano spettrogrammi
            print(f"\nSkipping \033[1m{labels_key}\033[0m as it is a label or has no valid data.")
            continue

        wave_condition_name = f'spectrograms_{condition_key}'
        print(f"\n\nResults for \t\t\t\t\t\033[1m{wave_condition_name}\033[0m:\n\n")

        # Converti in un array NumPy 3D finale
        spectrograms_4d = np.array(results['spectrograms'])  # Forma: (numero_di_trial, numero_canali, frequenze, tempo)
        all_subjects_condition_results[wave_condition_name] = {
            'spectrograms_4d': spectrograms_4d,
            'labels': results['labels']
        }

        print(f"spectrograms_4d shape: {spectrograms_4d.shape}")
    
    '''
    Quindi alla fine si avrà una shape del tipo (44, 61, 38, 7) dove indica che avrai
    uno spettrogramma per ciascun trial, per ciascun canale, 
    che contiene informazioni sulle bande di frequenza e sui punti temporali. 
    
    Questa struttura è perfetta per essere utilizzata come input per una rete neurale convoluzionale (CNN),
    poiché la rete può apprendere dalle relazioni spaziali e temporali nei dati.
    '''
    
    return all_subjects_condition_results


In [14]:
'''
CREAZIONE SPETTROGRAMMI ELETTRODI x FREQUENZE - VERSIONE UFFICIALE


Ti propongo una versione modificata della funzione che, per ogni soggetto e condizione, 
calcola la potenza spettrale tramite una FFT (usando np.fft.rfft) per ogni canale su un segmento specifico del segnale,
media i risultati sui trial e costruisce un’unica immagine 2D con:

Asse 0 (righe): vettore delle frequenze (ottenuto dalla FFT)
Asse 1 (colonne): elettrodi

In questo modo, per ogni soggetto e condizione avrai un’unica immagine in cui ogni “colonna” (cioè ogni elettrodo) 
mostra il vettore 1D delle potenze spettrali, come richiesto per poter interpretare successivamente il Grad-CAM.



Spiegazione delle modifiche

FFT anziché STFT:
Al posto di calcolare una STFT e poi aggregare nel tempo, ora per ogni canale si esegue una FFT sul segmento selezionato
(da segment_start a segment_end). La funzione np.fft.rfft restituisce solo i componenti a frequenza non negativa.

Aggregazione sui trial:

Per ciascun soggetto e condizione, 
i risultati della FFT ( = vettori di potenza spettrale), 
ossia il vettore ottenuto da ogni canale, viene impilato 
in modo da ottenere l'immagine di un trial. 
 
Ogni immagine rappresenta la potenza spettrale raccolta dalla FFT di ogni elettrodo di quel trial, e ogni immagine viene memorizzata separatamente.

Formazione dell’immagine:
I vettori di potenza di ciascun elettrodo vengono “impilati” in modo tale che, 
dopo la trasposizione, le righe rappresentino le frequenze e le colonne gli elettrodi. 

Questo formato permette al Grad-CAM di indicare quali frequenze e quali elettrodi risultano più discriminanti.

Questa funzione dovrebbe rispondere alle richieste del tuo supervisore, generando per ogni soggetto e condizione una sola immagine interpretabile con il Grad-CAM.


La funzione è stata progettata per rispettare quanto richiesto da Nicola. 

In particolare:

Calcolo per ogni elettrodo: Per ciascun canale (elettrodo) viene calcolata la FFT sul segmento specificato (da segment_start a segment_end), 
ottenendo un vettore 1D con la potenza spettrale in funzione della frequenza.

Aggregazione sui trial: 

Per ciascun soggetto e condizione, 
i risultati della FFT ( = vettori di potenza spettrale), 
ossia il vettore ottenuto da ogni canale, viene impilato 
in modo da ottenere l'immagine di un trial. 
 
Ogni immagine rappresenta la potenza spettrale raccolta dalla FFT di ogni elettrodo di quel trial, e ogni immagine viene memorizzata separatamente.

 
Creazione dell'immagine: 

Questi vettori, NON concatenati ma organizzati in colonne, vengono trasposti in modo da avere 

    - le righe rappresentanti le frequenze
    - le colonne gli elettrodi 
    
Così si ottiene, per ogni soggetto (e per ogni condizione) una singola immagine, 
che permette al Grad-CAM di evidenziare quali elettrodi (e quali frequenze) siano determinanti nel processo decisionale.

Se questo è esattamente quanto intendeva Nicola ("l'immagine sarebbe una sola per ogni soggetto" ottenuta raggruppando i vettori di ogni elettrodo), 
allora la funzione è adattata correttamente.


---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ----
RISULTATO FINALE:

1) Una immagine per ogni trial:
La variabile trial_power calcola la potenza spettrale per ciascun trial e la salva come una singola immagine (2D). 
    Queste immagini sono salvate nel dizionario condition_results[condition_key]['fft_images'] una per ciascun trial.

2) Shape dell'immagine:
Ogni immagine ha la forma (n_freq, n_channels), dove:

- n_freq è il numero di frequenze calcolato con np.fft.rfft.
- n_channels è il numero di elettrodi.

3) Etichette:
Se sono presenti le etichette per la condizione, vengono associate correttamente e stampate, come nel codice originale.

4) Dizionario finale:
Alla fine, il dizionario all_subjects_condition_results contiene un array 3D per ogni condizione (uno per ogni trial), con la forma 
    (n_trials, n_freq, n_channels).

Questo codice ora mantiene la logica originale di creare una immagine per ogni trial, mentre applica la FFT per calcolare la potenza spettrale. 

---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ----

'''


import numpy as np

def create_spectrograms_from_fft_images_of_electrodes(data, segment_start = 50, segment_end = 300, fs = 250, max_freq_bins=45):
    
    """
    Per ogni soggetto e condizione, calcola le immagini della potenza spettrale per ciascun elettrodo 
    usando la FFT (np.fft.rfft) sul segmento definito del segnale (per esempio l'intero trial).
    
    Per ogni trial, viene calcolata la FFT per ogni canale, ottenendo un vettore 1D di potenza spettrale.
    Viene poi tagliato lo spettro per mantenere solo le prime 'max_freq_bins' frequenze.
    
    Ogni trial genera un'immagine 2D (righe: frequenze, colonne: elettrodi) che viene memorizzata separatamente.
    
    Parameters:
        data (list di dict): Ogni dict corrisponde a un soggetto e contiene le condizioni sperimentali
                              (chiavi con dati in formato np.array di shape (n_trials, n_channels, n_timepoints))
                              e, eventualmente, le relative etichette (con chiave condition_labels).
        segment_start (int): Indice iniziale del segmento da analizzare.
        segment_end (int): Indice finale del segmento da analizzare.
        fs (int): Frequenza di campionamento.
        max_freq_bins (int): Numero massimo di frequenze da mantenere (ad es. le prime 45 frequenze).
    
    Returns:
        dict: Un dizionario in cui per ogni condizione sono memorizzati:
              - 'spectrograms_3d': array 3D contenente le immagini per ogni trial (shape: n_trials x max_freq_bins x n_channels)
              - 'labels': etichette associate (se presenti)
    """
    
    import numpy as np


    # Dizionario per memorizzare i risultati per ciascuna condizione sperimentale
    condition_results = {}
    
    for idx, data_dict in enumerate(data):
        print(f"\n\n\t\t\t\t\t\033[1mProcessing Subject {idx + 1}\033[0m:\n")
        
        for condition, value in data_dict.items():
            
            # Gestione delle chiavi per condizioni e relative label
            if '_labels' in condition:
                base_condition = condition.replace('_labels', '')
                condition_key = base_condition
                labels_key = condition
            else:
                base_condition = condition
                condition_key = base_condition
                labels_key = f'{base_condition}_labels'
            
            # Inizializza la struttura per la condizione se non esiste
            if '_labels' not in condition and condition_key not in condition_results:
                condition_results[condition_key] = {'fft_images': [], 'labels': []}
            
            if isinstance(value, np.ndarray):
                print(f"\nApplicazione FFT per '\033[1m{condition_key}\033[0m'\n")
                print(f"\033[1mShape\033[0m dei dati per \033[1m{condition_key}\033[0m: {value.shape}")
                
                # Presupponiamo che 'value' abbia forma: (n_trials, n_channels, n_timepoints)
                n_trials, n_channels, _ = value.shape
                
                N = segment_end - segment_start  # lunghezza del segmento analizzato
                
                n_freq = N // 2 + 1  # np.fft.rfft restituisce n_freq = N//2 + 1
                
                # Determina il numero di frequenze da utilizzare (taglia lo spettro)
                effective_freq_bins = min(n_freq, max_freq_bins)
                
                # Itera su ogni trial e ogni canale per calcolare la potenza spettrale
                for trial in range(n_trials):
                    
                    #trial_power = np.zeros((n_channels, n_freq))  # Matrice per la potenza per ogni trial
                    trial_power = np.zeros((n_channels, effective_freq_bins))  # Matrice per la potenza per ogni trial
                    
                    for channel in range(n_channels):
                        
                        # Estrai il segmento del segnale
                        single_channel_data = value[trial, channel, segment_start:segment_end]
                        
                        # Calcola la FFT (solo componenti a frequenza non negativa)
                        # -> https://numpy.org/doc/stable/reference/generated/numpy.fft.rfft.html
                        fft_vals = np.fft.rfft(single_channel_data)
                        
                        # Calcola la potenza spettrale (modulo al quadrato)
                        power = np.abs(fft_vals) ** 2
                        #trial_power[channel] = power
                        trial_power[channel] = power[:effective_freq_bins]
                    
                    # Trasponi in modo che le righe siano le frequenze e le colonne gli elettrodi
                    fft_image = trial_power.T  # shape: (n_freq, n_channels)
                    #print(f"FFT image shape for trial {trial + 1} of condition '{condition_key}': {fft_image.shape}")
                    
                    # Salva l'immagine per il trial corrente
                    #Ogni trial genera una sua immagine della potenza spettrale che viene memorizzata separatamente!
                    condition_results[condition_key]['fft_images'].append(fft_image)
                
                # Gestione delle etichette se presenti
                if labels_key in data_dict:
                    print(f"\nFound labels for condition \033[1m{labels_key}\033[0m, length: \033[1m{len(data_dict[labels_key])}\033[0m\n")
                    condition_results[condition_key]['labels'].extend(data_dict[labels_key])
                
            else:
                print(f"\033[1m{labels_key}\033[0m non è un np.array, non applicare la FFT ")
    
    # Riorganizza i risultati in un dizionario finale
    all_subjects_condition_results = {}
    for condition_key, results in condition_results.items():
        if "_labels" in condition_key or len(results['fft_images']) == 0:
            print(f"\nSkipping \033[1m{condition_key}\033[0m as it is a label or has no valid data.")
            continue
        
        wave_condition_name = f'spectrograms_{condition_key}'
        print(f"\n\nResults for \t\t\t\t\t\033[1m{wave_condition_name}\033[0m:\n\n")
        
        # Ogni trial produce un'immagine 2D di shape (n_freq, n_channels)
        spectrograms_3d = np.array(results['fft_images'])
        all_subjects_condition_results[wave_condition_name] = {
            'spectrograms_3d': spectrograms_3d,
            'labels': results['labels']
        }
        print(f"spectrograms_3d shape for {wave_condition_name}: {spectrograms_3d.shape}")
    
    return all_subjects_condition_results


#new_all_subjects_condition_spectrograms_th = create_spectrograms_from_fft_images_of_electrodes (therapists_data, segment_start = 50, segment_end = 300, fs=250, max_freq_bins=45)

In [ ]:
# Richiamo della funzione per processare tutti i soggetti e ottenere i risultati per ciascuna condizione
#new_all_subjects_condition_spectrograms_th = create_spectograms_from_stft_electrode_freq (therapists_data, window_size  = 50, step_size = 25, fs=250)#

In [ ]:
# Richiamo della funzione per processare tutti i soggetti e ottenere i risultati per ciascuna condizione
#new_all_subjects_condition_spectrograms_th = create_spectograms_from_stft(therapists_data, window_size=50, step_size=25, fs=250)

In [15]:
new_all_subjects_condition_spectrograms_th = create_spectrograms_from_fft_images_of_electrodes (therapists_data, segment_start = 50, segment_end = 300, fs=250, max_freq_bins=45)



					Processing Subject 1:


Applicazione FFT per 'baseline_1'

Shape dei dati per baseline_1: (44, 61, 300)

Found labels for condition baseline_1_labels, length: 44


Applicazione FFT per 'th_resp_1'

Shape dei dati per th_resp_1: (40, 61, 300)

Found labels for condition th_resp_1_labels, length: 40


Applicazione FFT per 'pt_resp_1'

Shape dei dati per pt_resp_1: (43, 61, 300)

Found labels for condition pt_resp_1_labels, length: 43


Applicazione FFT per 'shared_resp_1'

Shape dei dati per shared_resp_1: (47, 61, 300)

Found labels for condition shared_resp_1_labels, length: 47

baseline_1_labels non è un np.array, non applicare la FFT 
th_resp_1_labels non è un np.array, non applicare la FFT 
pt_resp_1_labels non è un np.array, non applicare la FFT 
shared_resp_1_labels non è un np.array, non applicare la FFT 


					Processing Subject 2:


Applicazione FFT per 'baseline_2'

Shape dei dati per baseline_2: (60, 61, 300)

Found labels for condition baseline_2_labels, length: 60



In [16]:
print('finito')

finito


In [17]:
new_all_subjects_condition_spectrograms_th.keys()

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [18]:
#new_all_subjects_condition_spectrograms_th['spectrograms_baseline_1']['spectrograms_4d'].shape
new_all_subjects_condition_spectrograms_th['spectrograms_baseline_1']['spectrograms_3d'].shape

(44, 45, 61)

In [19]:
#Salvo ricostruzioni 4° e 5° livello terapisti

'''PATH  --> cd Plots_Sliding_Estimator_MNE'''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('all_subjects_condition_results_th.pkl', 'wb') as f:
#    pickle.dump(all_subjects_condition_results_th, f)
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

import pickle

# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_all_subjects_condition_spectrograms_th_2D.pkl', 'wb') as f:
    pickle.dump(new_all_subjects_condition_spectrograms_th, f)

In [20]:
new_all_subjects_condition_spectrograms_th.keys()

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [21]:
new_all_subjects_condition_spectrograms_th['spectrograms_baseline_1'].keys()

dict_keys(['spectrograms_3d', 'labels'])

In [22]:
#new_all_subjects_condition_spectrograms_th['spectrograms_baseline_1']['spectrograms_4d'].shape
new_all_subjects_condition_spectrograms_th['spectrograms_baseline_1']['spectrograms_3d'].shape

(44, 45, 61)

#### Esempi di Plots da Un Trial, Una Condizionizione Sperimentale, Un Canale EEG

In [ ]:
'''
Il tempo che vedi nell'asse X non è espresso direttamente in termini di punti EEG, 
ma nel dominio delle finestre scorrevoli (che sono di 75 punti con uno shift di 25 punti).


Questo codice  considera l'inizio della finestra STFT come riferimento per il tempo.
'''

import matplotlib.pyplot as plt

# Estrarre il primo soggetto e la prima condizione
first_condition_key = list(new_all_subjects_condition_spectrograms_th.keys())[0]
spectrograms = new_all_subjects_condition_spectrograms_th[first_condition_key]['spectrograms_4d']

# Selezionare il primo trial e il primo canale
trial_index = 0
channel_index = 0
spectrogram = np.abs(spectrograms[trial_index, channel_index, :, :])  # Prendere il modulo dello spettrogramma

# Ricavare frequenze e intervalli temporali dalla STFT
fs = 250  # Frequenza di campionamento EEG
window_size = 75
step_size = 25

f, t = np.linspace(0, fs / 2, spectrogram.shape[0]), np.arange(spectrogram.shape[1])  # Indici di tempo grezzi

# Convertire gli intervalli temporali da campioni EEG a millisecondi
t_ms = -200 + (t * step_size * (1000 / fs))  # -200 ms è il tempo di prestimolo iniziale

# Creare il plot
plt.figure(figsize=(10, 6))
plt.pcolormesh(t_ms, f, spectrogram, shading='auto', cmap='jet')
plt.colorbar(label='Amplitude')
plt.xlabel('Time (ms)')
plt.ylabel('Frequency (Hz)')
plt.title(f'Spectrogram - {first_condition_key} - Trial {trial_index+1} - Channel {channel_index+1}')
plt.axvline(0, color='k', linestyle='--', label="Stimulus onset")
plt.legend()
plt.show()


In [ ]:
'''

Questo Codice considera il centro della finestra come riferimento.
Ossia, è più rappresentativo rispetto alla stft di ogni finestra in sostanza, 
cioè fornisce una visualizzazione migliore delle componenti frequenziali del segnale in funzione di quella finestra per cui è stata fatta la stft?


Perché è più corretto?
Quando calcoli la STFT, la trasformata viene effettuata su una finestra mobile di lunghezza window_size (75 campioni). 
Il risultato della STFT rappresenta il contenuto in frequenza della finestra nel suo complesso, non solo il punto iniziale della finestra.

Nel Codice 1, il tempo è allineato con l'inizio della finestra, il che può dare un’impressione leggermente distorta:

La STFT a t = -200 ms viene plottata come se rappresentasse solo il segnale in quel momento, ma in realtà include informazioni da -200 ms a -100 ms.
Nel Codice 2, invece, il tempo è allineato con il centro della finestra, il che è più rappresentativo:

La STFT calcolata sulla finestra [-200, -100] ms viene plottata a t = -150 ms, che è il centro effettivo della finestra.
Vantaggi della rappresentazione nel Codice 2
✅ Ogni punto temporale dello spettrogramma mostra il contenuto in frequenza della finestra corrispondente, e non di un singolo istante.
✅ La rappresentazione è più coerente con l’effettivo contributo temporale delle finestre, migliorando la leggibilità.
✅ Se si vuole confrontare i risultati con altri metodi di analisi nel dominio del tempo (es. ERP), questa rappresentazione è più affidabile.

📌 Conclusione:
Sì, il Codice 2 fornisce una visualizzazione più accurata delle componenti frequenziali di ogni finestra STFT, 
perché mostra i risultati nel punto temporale più rappresentativo per ogni finestra.


'''

import matplotlib.pyplot as plt
import numpy as np

# Seleziona la prima condizione sperimentale
first_condition = list(new_all_subjects_condition_spectrograms_th.keys())[0]

# Estrai gli spettrogrammi per la condizione selezionata
spectrograms_4d = new_all_subjects_condition_spectrograms_th[first_condition]['spectrograms_4d']

# Seleziona il primo trial e il primo canale
trial_idx = 0
channel_idx = 0
spectrogram_trial_channel = np.abs(spectrograms_4d[trial_idx, channel_idx, :, :])  # Modulo della STFT

# Definizione dei parametri
fs = 250  # Frequenza di campionamento (Hz)
window_size = 75  # Lunghezza della finestra STFT (punti EEG)
step_size = 25  # Spostamento tra finestre (punti EEG)

# Crea asse delle frequenze e del tempo in ms
frequencies = np.linspace(0, fs / 2, spectrogram_trial_channel.shape[0])  # Frequenze in Hz
time_points = ((np.arange(spectrogram_trial_channel.shape[1]) * step_size) + (window_size // 2)) * 4 - 200  # Tempo in ms

# Plot dello spettrogramma
plt.figure(figsize=(10, 6))
plt.pcolormesh(time_points, frequencies, spectrogram_trial_channel, shading='auto', cmap='jet')
plt.colorbar(label='Magnitudine')
plt.xlabel('Tempo (ms)')
plt.ylabel('Frequenza (Hz)')
plt.axvline(x=0, color='k', linestyle='--', label='Stimolo')  # Linea verticale sullo stimolo
plt.title(f'Spettrogramma - {first_condition} (Trial {trial_idx+1}, Canale {channel_idx+1})')
plt.legend()
plt.show()


#### **Concatenazione** All **SINGLE** Subject **Spectrograms (TH)** per **Tutte le Condizioni Sperimentali**

In [23]:
new_all_subjects_condition_spectrograms_th.keys()

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [24]:
import numpy as np

# Definizione degli indici dei canali desiderati

'''TOLGO PER SPETTROGRAMMI FREQUENZE x ELETTRODI'''
#selected_channels = [12, 30, 48]  # Indici per Fz, Cz, Pz

# Creazione di un dizionario dei dati di tutti i terapisti singolarmente, per salvare gli spettrogrammi calcolati
new_single_th_all_extracted_spectrograms_2D = {}

# Iterazione su tutte le condizioni sperimentali di tutti i soggetti 

for condition, data in new_all_subjects_condition_spectrograms_th.items():
    
    # Estrarre le etichette per la condizione corrente
    labels = data['labels']
    
    #  Estrarre gli spettrogrammi per la condizione corrente
    '''TOLGO PER SPETTROGRAMMI FREQUENZE x ELETTRODI'''
    #spectrograms = data['spectrograms_4d']
    
    spectrograms = data['spectrograms_3d']
    
    '''TOLGO PER SPETTROGRAMMI FREQUENZE x ELETTRODI'''
    #Selezione dei canali di interesse (Fz, Cz e Pz)
    #spectrograms = spectrograms[:, selected_channels, :, :]
    
    new_single_th_all_extracted_spectrograms_2D[condition] = {
        'spectrograms': spectrograms,
        #'delta': delta_reconstruction,
        #'coeff_fifth_detail_theta': coeff_fifth_detail_theta, 
        'labels': labels
    }
    
# Verifica delle dimensioni del risultato estratto per una condizione specifica di ogni soggetto
print(f"\t\t\033[1mEstrazione Spettrogrammi di tutti i terapisti per tutte le condizioni sperimentali")
print(f"\n\n\t\t\t\t(i.e., \033[1mnew_single_th_all_extracted_spectrograms_2D\033[0m):\n")

for condition, extracted_data in new_single_th_all_extracted_spectrograms_2D.items():
    
    print(f"Condizione: \033[1m{condition}\033[0m, "
          f"Spectrograms shape: \033[1m{extracted_data['spectrograms'].shape}\033[0m, "
          f"Labels: \033[1m{len(extracted_data['labels'])}\033[0m")

		Estrazione Spettrogrammi di tutti i terapisti per tutte le condizioni sperimentali


				(i.e., new_single_th_all_extracted_spectrograms_2D):

Condizione: spectrograms_baseline_1, Spectrograms shape: (44, 45, 61), Labels: 44
Condizione: spectrograms_th_resp_1, Spectrograms shape: (40, 45, 61), Labels: 40
Condizione: spectrograms_pt_resp_1, Spectrograms shape: (43, 45, 61), Labels: 43
Condizione: spectrograms_shared_resp_1, Spectrograms shape: (47, 45, 61), Labels: 47
Condizione: spectrograms_baseline_2, Spectrograms shape: (60, 45, 61), Labels: 60
Condizione: spectrograms_th_resp_2, Spectrograms shape: (40, 45, 61), Labels: 40
Condizione: spectrograms_pt_resp_2, Spectrograms shape: (43, 45, 61), Labels: 43
Condizione: spectrograms_shared_resp_2, Spectrograms shape: (61, 45, 61), Labels: 61
Condizione: spectrograms_baseline_3, Spectrograms shape: (57, 45, 61), Labels: 57
Condizione: spectrograms_th_resp_3, Spectrograms shape: (39, 45, 61), Labels: 39
Condizione: spectrograms_pt_resp_3

In [25]:
'''Salvataggio di new_single_th_all_extracted_spectrograms_2D'''

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

import pickle

# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_single_th_all_extracted_spectrograms_2D.pkl', 'wb') as f:
    pickle.dump(new_single_th_all_extracted_spectrograms_2D, f)

In [26]:
new_single_th_all_extracted_spectrograms_2D.keys()

new_single_th_all_extracted_spectrograms_2D['spectrograms_baseline_1'].keys()

dict_keys(['spectrograms', 'labels'])

In [27]:
'''
Questa struttura consente di avere i dati degli spettrogrammi correttamente organizzati e concatenati per ogni soggetto,
mantenendo la corrispondenza tra dati e etichette per ogni condizione sperimentale

Da           "single_th_all_extracted_reconstructions"       a           "subject_level_concatenations_th"

Da           "new_single_th_all_extracted_reconstructions"       a       "new_subject_level_concatenations_th"

Da           "new_single_th_all_extracted_spectrograms_2D"       a       "new_subject_level_concatenations_spectrograms_th_2D"
'''


# Dizionario per contenere i dati concatenati per ogni soggetto
new_subject_level_concatenations_spectrograms_th_2D = {}

# Variabile per tracciare il soggetto precedente
previous_subject_suffix = None

print(f"\t\t\033[1mConcatenazione spettrogrammi 2D per OGNI soggetto di TUTTE le condizioni sperimentali INSIEME\033[0m")

# Iterazione su tutte le chiavi di new_single_th_all_extracted_spectrograms_2D
for condition, data in new_single_th_all_extracted_spectrograms_2D.items():
    
    # Estrazione del suffisso numerico del soggetto
    subject_suffix = condition.split('_')[-1]  # Prende solo la parte numerica
    
    # Creazione del nome della chiave del soggetto specifico
    subj_name = f'th_{subject_suffix}'
    
    # Se stiamo per passare a un nuovo soggetto, concatenare e stampare i risultati del soggetto precedente
    if previous_subject_suffix is not None and subject_suffix != previous_subject_suffix:
        
        print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('th_{previous_subject_suffix}'):\033[0m\n")
        prev_subject_name = f'th_{previous_subject_suffix}'
        levels = new_subject_level_concatenations_spectrograms_th_2D[prev_subject_name]

        # Concatenazione dei dati prima della stampa
        spectrograms_concat = np.concatenate(levels['spectrograms'], axis=0)
        labels_concat = np.concatenate(levels['labels'], axis=0)

        print(f"Soggetto: \033[1m{prev_subject_name}\033[0m, "
              f"Spettrogrammi shape: \033[1m{spectrograms_concat.shape}\033[0m, "
              f"Labels length: \033[1m{len(labels_concat)}\033[0m")
        
        # Salvataggio dei dati concatenati nel dizionario
        new_subject_level_concatenations_spectrograms_th_2D[prev_subject_name]['spectrograms'] = spectrograms_concat
        new_subject_level_concatenations_spectrograms_th_2D[prev_subject_name]['labels'] = labels_concat
    
    # Inizializzare il dizionario per il soggetto specifico se non esiste già
    if subj_name not in new_subject_level_concatenations_spectrograms_th_2D:
        new_subject_level_concatenations_spectrograms_th_2D[subj_name] = {
            'spectrograms': [],
            'labels': []
        }
    
    # Stampiamo le informazioni per ogni condizione
    print(f"\n\n\nSoggetto: \033[1m{subj_name}\033[0m, Condizione: \033[1m{condition}\033[0m")
    print(f"  - Spettrogrammi shape: \033[1m{data['spectrograms'].shape}\033[0m")
    print(f"  - Labels shape: \033[1m{len(data['labels'])}\033[0m")
    print(f"  - Valore unico delle etichette: \033[1m{np.unique(data['labels'])}\033[0m")
    
    # Concatenazione dei dati
    new_subject_level_concatenations_spectrograms_th_2D[subj_name]['spectrograms'].append(data['spectrograms'])
    new_subject_level_concatenations_spectrograms_th_2D[subj_name]['labels'].append(data['labels'])
    
    # Aggiorna il soggetto precedente
    previous_subject_suffix = subject_suffix

# Dopo aver iterato su tutte le condizioni, concatenare e stampare le informazioni dell'ultimo soggetto
if previous_subject_suffix is not None:
    
    last_subject_name = f'th_{previous_subject_suffix}'
    levels = new_subject_level_concatenations_spectrograms_th_2D[last_subject_name]
    
    print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('{last_subject_name}'):\033[0m\n")
    
    # Concatenazione dei dati dell'ultimo soggetto
    spectrograms_concat = np.concatenate(levels['spectrograms'], axis=0)
    labels_concat = np.concatenate(levels['labels'], axis=0)
    
    # Salvataggio dei dati concatenati dell'ultimo soggetto nel dizionario
    new_subject_level_concatenations_spectrograms_th_2D[last_subject_name] = {
        'spectrograms': spectrograms_concat,
        'labels': labels_concat
    }
    
    print(f"Soggetto: \033[1m{last_subject_name}\033[0m, "
          f"Spettrogrammi shape: \033[1m{spectrograms_concat.shape}\033[0m, "
          f"Labels length: \033[1m{len(labels_concat)}\033[0m\n\n")


		Concatenazione spettrogrammi 2D per OGNI soggetto di TUTTE le condizioni sperimentali INSIEME



Soggetto: th_1, Condizione: spectrograms_baseline_1
  - Spettrogrammi shape: (44, 45, 61)
  - Labels shape: 44
  - Valore unico delle etichette: ['0']



Soggetto: th_1, Condizione: spectrograms_th_resp_1
  - Spettrogrammi shape: (40, 45, 61)
  - Labels shape: 40
  - Valore unico delle etichette: ['1']



Soggetto: th_1, Condizione: spectrograms_pt_resp_1
  - Spettrogrammi shape: (43, 45, 61)
  - Labels shape: 43
  - Valore unico delle etichette: ['2']



Soggetto: th_1, Condizione: spectrograms_shared_resp_1
  - Spettrogrammi shape: (47, 45, 61)
  - Labels shape: 47
  - Valore unico delle etichette: ['3']


				Concatenazioni per il soggetto corrente ('th_1'):

Soggetto: th_1, Spettrogrammi shape: (174, 45, 61), Labels length: 174



Soggetto: th_2, Condizione: spectrograms_baseline_2
  - Spettrogrammi shape: (60, 45, 61)
  - Labels shape: 60
  - Valore unico delle etichette: ['0']



So

In [28]:
'''CHIAVI DI TUTTO IL DIZIONARIO '''
#subject_level_concatenations_th.keys()


new_subject_level_concatenations_spectrograms_th_2D.keys()


#SOGGETTO 1

#CHIAVI
#subject_level_concatenations_th['th_1'].keys()

#DATI
#subject_level_concatenations_th['th_1']['theta'].shape

#new_subject_level_concatenations_th['th_1']['theta'].shape

#subject_level_concatenations_th['th_1']['delta'].shape

#LABELS
#subject_level_concatenations_th['th_1']['labels'].shape)
#type(subject_level_concatenations_th['th_1']['labels'])

# Check della concantenazione delle labels TH_1

#subject_level_concatenations_th['th_1']['labels'][:42]
#subject_level_concatenations_th['th_1']['labels'][41:81]
#subject_level_concatenations_th['th_1']['labels'][81:120]
#subject_level_concatenations_th['th_1']['labels'][121:164]

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16', 'th_17', 'th_18', 'th_19', 'th_20'])

In [ ]:
#subject_level_concatenations_th['th_15']['labels'].shape

In [29]:
#subject_level_concatenations_th['th_1'].keys()

new_subject_level_concatenations_spectrograms_th_2D['th_1'].keys()


dict_keys(['spectrograms', 'labels'])

In [30]:
#unique_values, counts = np.unique(subject_level_concatenations_th['th_1']['labels'], return_counts=True)

#unique_values, counts = np.unique(new_subject_level_concatenations_th['th_1']['labels'], return_counts=True)

In [31]:
#unique_values
#counts
#counts[0]

In [32]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [33]:
#Salvo ricostruzioni 4° e 5° livello per singolo terapista con concatenazioni dati e labels 

''' PATH  --> cd Plots_Sliding_Estimator_MNE '''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('subject_level_concatenations_pt.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations_pt, f)
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_1_45_NF '''

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

import pickle

# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_subject_level_concatenations_spectrograms_th_2D.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_spectrograms_th_2D, f)

#### **Concatenazione** All **SINGLE** Subject **Spectrograms (TH)** per **Coppie di Condizioni Sperimentali**

In [34]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [35]:
cd ..

/home/stefano/Interrogait


In [36]:
cd New_Plots_Sliding_Estimator_MNE_1_45/

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [37]:
import pickle
import numpy as np

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'


fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_single_th_all_extracted_spectrograms_2D.pkl', 'rb') as f:
    new_single_th_all_extracted_spectrograms_2D = pickle.load(f)

In [38]:
new_single_th_all_extracted_spectrograms_2D.keys()

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [39]:
new_single_th_all_extracted_spectrograms_2D['spectrograms_baseline_1'].keys()

dict_keys(['spectrograms', 'labels'])

##### Spiegazione STEP - Concatenazione All Single Subject Spectrograms (TH) across Couples of Experimental Conditions

###### **Concatenazione All Single Subject Data (TH) per Coppie di Condizioni Sperimentali**

<br>

In questo caso, voglio **trasformare le variabili che contengono i miei dati e labels delle 4 condizioni sperimentali assieme**, in modo **da creare sottoinsiemi per ogni possibile coppia di condizioni sperimentali**. 

Dunque quello che si dovrà fare **per ogni coppia**:

1) **Filtrare i dati e le etichette**:

- **Estrarre** i dati associati **SOLO alle DUE condizioni in esame** (ad esempio 0 e 1, oppure 1 e 2).
- **Creare un nuovo array di etichette** e **un array di dati** ***corrispondenti*** **SOLO a quelle DUE condizioni**.

2) **Ripetere questa operazione per OGNI combinazione**:

- **Assicurarsi di considerare tutte le coppie** di condizioni sperimentali **SENZA ripetizioni** (ad esempio, non serve processare sia 0 vs 1 che 1 vs 0, perché sono equivalenti!).

3) **Creare quindi una struttura organizzata**, che contenga i dati e le etichette separatamente per ogni coppia, per ciascun livello di ricostruzione (theta, delta, theta_strict).

<br>

Quindi l'obiettivo è di modificare la procedura in modo da **concatenare SOLO le coppie di condizioni sperimentali per OGNI soggetto**. 

Per fare questo, possiamo utilizzare un **approccio combinatorio** per generare **tutte le possibili coppie di condizioni**.


Per quanto riguarda il calcolo combinatorio, possiamo usare il concetto di combinazioni per selezionare le coppie. 
Se hai 4 condizioni, il numero di combinazioni di coppie di condizioni (senza ripetizioni) si calcola come:

$$
\binom{4}{2} = \frac{4!}{2!(4-2)!} = 6
$$


Quindi, con 4 condizioni sperimentali, le combinazioni di coppie di condizioni saranno 6, e queste coppie sono:

(condizione 1, condizione 2) = 'baseline vs th_resp'
(condizione 1, condizione 3) = 'baseline vs pt_resp'
(condizione 1, condizione 4) = 'baseline vs shared_resp'
(condizione 2, condizione 3) = 'th_resp vs pt_resp'
(condizione 2, condizione 4) = 'th_resp vs shared_resp'
(condizione 3, condizione 4) = 'pt_resp vs shared_resp' 


<br>

Piano di modifiche al codice:

1) **Creazione delle coppie di condizioni**: Per ogni soggetto, genereremo tutte le coppie possibili di condizioni sperimentali. Utilizzeremo itertools.combinations per ottenere queste coppie.

2) **Concatenazione per ciascuna coppia**: Per ogni coppia di condizioni, concatenare i dati e le etichette delle due condizioni selezionate.

3) **Salvataggio delle concatenazioni**: Creeremo un dizionario per ciascuna coppia di condizioni per ogni soggetto.


**N.B.**

Nel codice che sto creando...

Ho fatto in modo che ci sia il modo di capire, **per ogni coppia di condizione sperimentale di dati e labels**, a quali condizione sperimentali di dati e labels ci si riferisca, mi spiego:

Sviluppo un **modo "standardizzato" per il quale per OGNI coppia di condizione sperimentale, la variabile che conterrà i dati e labels associate, sia chiamata in un certo modo**...

E nello specifico **con il nome delle DUE condizioni sperimentali che conterranno quei dati e relative labels**...

Del tipo: 

- se è baseline vs th_resp, la variabile sarà "baseline_vs_th_resp"
- se è baseline vs pt_resp, la variabile sarà "baseline_vs_pt_resp"
- se è baseline vs shared_resp, la variabile sarà "baseline_vs_shared_resp"


Senza contare che, questo **processo di standardizzazione del nome delle variabili**, deve esser fatto **per ogni livello di ricostruzione dei dati (sia 4° e 5° livello a partire dai coefficienti di approssimazione, che dal 5 ° livello dei coefficienti di dettaglio)**..

Questo significherebbe che, **per ogni soggetto**, dovrei (o potrei insomma) creare **un dizionario**, che 

- Contenga delle **sotto-chiavi di secondo ordine** (che son theta, delta e theta_strict) e dentro ognuna di queste
- Ci siano contenute **le relative 6 sotto-sotto-chiavi di terzo ordine**, relative ai dati e alle labels associate (anch'esse concatenate ovviamente) delle diverse combinazioni di condizioni sperimentali...


Ossia, vogliamo creare un dizionario strutturato che rappresenti ogni combinazione di coppie di condizioni sperimentali per ciascun soggetto, separando i dati e le etichette per i vari livelli di ricostruzione (theta, delta, theta_strict). 

Ogni combinazione di condizioni sperimentali sarà memorizzata in una chiave strutturata, come ad esempio "baseline_vs_th_resp", e all'interno di ciascuna chiave avremo le informazioni per i vari livelli di ricostruzione.


<br>


#### Esempio di Struttura proposta per il dizionario:


- Soggetto: ad esempio "th_1".
- Livelli di ricostruzione: theta, delta, theta_strict.
- Combinazioni di condizioni sperimentali: per ciascun livello di ricostruzione, avremo sotto-chiavi per ogni coppia di condizioni.

        new_subject_level_concatenations = {
            'th_1': {
                'theta': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                },
                'delta': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                },
                'theta_strict': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                }
            }
        }

<br>

**SOTTO-STEP 1: IDENTIFICAZIONE DELLE STRINGA NUMERICHE PER LA CREAZIONE DELLE VARIABILI - FUTURE CHIAVI - CHE CONTENGONO LE COPPIE DI DATI E LABELS DELLE RELATIVE COPPIE DI CONDIZIONI SPERIMENTALI CONSIDERATE NEL CICLO CORRENTE DEL LOOP**

Aspetta, ci sono altre cose che dovrebbero esser integrate nel codice...

cominciamo dalla prima, che è relativa all' "inferire" diciamo il nome da fornire alla variabile che conterrà i dati e labels delle due condizioni sperimentali correnti... e deve esser fatto, a partire dal nome delle chiavi di 

"new_single_th_all_extracted_reconstructions"...

ora, le sue chiavi son queste

dict_keys(['wave_baseline_1', 'wave_th_resp_1', 'wave_pt_resp_1', 'wave_shared_resp_1', 'wave_baseline_2', 'wave_th_resp_2', 'wave_pt_resp_2', 'wave_shared_resp_2', 'wave_baseline_3', 'wave_th_resp_3', 'wave_pt_resp_3', 'wave_shared_resp_3', 'wave_baseline_4', 'wave_th_resp_4', 'wave_pt_resp_4', 'wave_shared_resp_4', 'wave_baseline_5', 'wave_th_resp_5', 'wave_pt_resp_5', 'wave_shared_resp_5', 'wave_baseline_6', 'wave_th_resp_6', 'wave_pt_resp_6', 'wave_shared_resp_6', 'wave_baseline_7', 'wave_th_resp_7', 'wave_pt_resp_7', 'wave_shared_resp_7', 'wave_baseline_8', 'wave_th_resp_8', 'wave_pt_resp_8', 'wave_shared_resp_8', 'wave_baseline_9', 'wave_th_resp_9', 'wave_pt_resp_9', 'wave_shared_resp_9', 'wave_baseline_10', 'wave_th_resp_10', 'wave_pt_resp_10', 'wave_shared_resp_10', 'wave_baseline_11', 'wave_th_resp_11', 'wave_pt_resp_11', 'wave_shared_resp_11', 'wave_baseline_12', 'wave_th_resp_12', 'wave_pt_resp_12', 'wave_shared_resp_12'])


ora, il modo in cui si identifica un certo soggetto (ossia la chiavi di "primo ordine" che indentificano il soggetto, ossia ad esempio 'th_1'), dipenderebbe dal numero stringa che c'è alla fine di ogni nome stringa di ogni chiave dentro "new_single_th_all_extracted_reconstructions", mi spiego:

il codice dovrebbe capire che, ad esempio, solo l'ultima carattere stringa di queste prime 4 chiavi:

'wave_baseline_1', 'wave_th_resp_1', 'wave_pt_resp_1', 'wave_shared_resp_1', 

si riferisca al soggetto 1, ossia al futuro "th_1"...


per il soggetto 2, sarebbero: 

'wave_th_resp_2', 'wave_pt_resp_2', 'wave_shared_resp_2', e così via per gli altri soggetti..


Facendo attenzione al fatto che, dopo il soggetto 9, ovviamente, si passerà alle decine (a livello numerico), per cui saranno gli ultime due caratteri da considerare per l'identificazione delle sue rispettive chiavi, che in quel caso saranno per il soggetto 10, ossia il futuro th_10

'wave_baseline_10', 'wave_th_resp_10', 'wave_pt_resp_10', 'wave_shared_resp_10',

Inoltre, poi, per creare le variabili associate alle coppie di dati e labels delle relative condizioni sperimentali, dovrà il codice far in modo che il nome di quella variabile dipenda dalle stringhe sempre che si riferiscono al nome delle due chiavi di "new_single_th_all_extracted_reconstructions" da cui preleva i dati e le labels... 

ad esempio, se deve creare la variabile dei dati 'baseline_vs_th_resp" del primo soggetto, le chiavi rispettive da cui deve andare a prelevare le stringhe saranno appunto "'wave_baseline_1'" e "'wave_th_resp_1'"....

diciamo che si potrebbe creare una lista di stringhe che sarà del tipo:

experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp'], per vedere se una di queste sia dentro la rispettiva chiave di  new_single_th_all_extracted_reconstructions su cui sta iterando, che nel nostro caso di esempio sarebbero sempre

'wave_baseline_1' (e da cui vede che c'è la stinga 'baseline')
'wave_th_resp_1' (e da cui vede che c'è la stinga 'th_resp')

è chiaro?


<br>

In sostanza, desideri un modo per inferire dinamicamente il nome del soggetto e delle variabili che conterranno i dati e le etichette per ogni combinazione di condizioni, a partire dal nome delle chiavi di new_single_th_all_extracted_reconstructions. Ecco un piano per raggiungere questo obiettivo:

Passaggi:

- Identificare il soggetto:

Le chiavi di new_single_th_all_extracted_reconstructions finiscono con un numero che identifica il soggetto (es. wave_baseline_1, wave_th_resp_1, wave_pt_resp_1).
Questo numero può essere estratto dalle ultime cifre della chiave (ad esempio, 1 da wave_baseline_1).
La variabile associata a ciascun soggetto sarà chiamata th_X, dove X è il numero del soggetto.

- Generare dinamicamente il nome delle variabili:

A partire dai nomi delle chiavi, possiamo inferire quale combinazione di condizioni sperimentali stiamo trattando (es. baseline_vs_th_resp).
Creeremo una lista delle condizioni (experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']), quindi esamineremo le chiavi per determinare quali condizioni sono presenti.

- Creare il dizionario:

A ciascun soggetto verrà associato un dizionario, e per ogni combinazione di condizioni sperimentali, assoceremo i dati e le etichette in una chiave che seguirà la convenzione del tipo baseline_vs_th_resp.


<br>

Spiegazione:

1) Estrazione delle condizioni e soggetto:

La chiave, ad esempio wave_baseline_1, viene separata in parti. La parte baseline viene estratta per determinare la condizione, mentre 1 indica il numero del soggetto.
Queste informazioni vengono utilizzate per creare il nome del soggetto, th_1.

2) Combinazioni di condizioni:

La lista experimental_conditions contiene le 4 condizioni: baseline, th_resp, pt_resp, shared_resp.
Per ogni soggetto, controlliamo quali condizioni sono disponibili nella chiave (ad esempio, se il soggetto 1 ha wave_baseline_1 e wave_th_resp_1, creiamo la combinazione baseline_vs_th_resp).

3) Creazione dinamica delle variabili:

Utilizziamo la combinazione di condizioni per generare la chiave della variabile (baseline_vs_th_resp).
I dati e le etichette per la combinazione di condizioni vengono estratti e concatenati.


4) Risultato finale:

La struttura finale del dizionario new_subject_level_concatenations avrà una chiave per ciascun soggetto (th_1, th_2, ecc.), e sotto ogni soggetto ci saranno le combinazioni di condizioni per ciascun livello di ricostruzione (theta, delta, theta_strict), con i dati e le etichette corrispondenti.

<br>

Esempio di output:

    {
        'th_1': {
            'theta': {
                'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'th_resp_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                # Altre combinazioni...
            },
            'delta': {
                # Stessa struttura per 'delta'
            },
            'theta_strict': {
                # Stessa struttura per 'theta_strict'
            }
        }
    }

 
Questa struttura ti permetterà di avere un'organizzazione chiara e dinamica dei dati per ogni soggetto e combinazione di condizioni sperimentali.
 
 
<br>

**SOTTO-STEP 2: IDENTIFICAZIONE DELLE STRINGA ALFABETICHE PER LA CREAZIONE DELLE VARIABILI - FUTURE CHIAVI - CHE CONTENGONO IL NOME DELLE DUE COPPIE DI CONDIZIONI SPERIMENTALI DI CUI VENGONO PRELEVATI I DATI E LABELS CONCATENATI E CHE VENGONON CONSIDERATE NEL CICLO CORRENTE DEL LOOP**


ok, ora c'è una ultima cosa che mi manca da dirti, che è relativa alla ri-assegnazione del codice numerico associato ad ogni coppia di condizioni sperimentali...

nel senso che, originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò 

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo


print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n")
print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n")
print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n")
print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")


Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza,  nel tuo codice, ho bisogno che 

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre 

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e  e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare le labels andranno ovviamente riconvertite! Perché?
perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempip, in quel caso, le sue labels (che son  originariamente codificate come '1' in 'new_subject_level_concatenations'!) diveteranno '0', mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...


è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?


<br>

La **logica di ri-assegnazione delle etichette (labels)** è chiara e posso integrarla nel codice. 

La logica che stai descrivendo consiste essenzialmente nel **garantire che, quando crei una variabile che contiene dati e etichette per due condizioni sperimentali, le etichette siano sempre "0" per la prima condizione (cond_1) e "1" per la seconda condizione (cond_2)**, 

                **INDIPENDENTEMENTE** da come sono originariamente codificate in **"new_single_th_all_extracted_reconstructions"!
                
                

Ecco come possiamo procedere:

- Identificazione delle condizioni: Come hai descritto, determineremo le due condizioni sperimentali da confrontare, ad esempio "baseline" contro "th_resp", "baseline" contro "pt_resp", ecc.

- Riconversione delle etichette:

 - Se la condizione di confronto è "baseline" (che è associata a 0), non dobbiamo modificare le etichette.
 - Se la condizione di confronto non è "baseline", dovremo riconvertire le etichette di quella condizione a 0 e le etichette della condizione di confronto a 1.

- Struttura del codice: Durante la creazione delle variabili, dovremo controllare quale condizione è la prima (cond_1) e quale è la seconda (cond_2), e applicare questa logica per ri-assegnare le etichette di conseguenza.


<br>

Inoltre


dentro 

"# Crea tutte le combinazioni uniche di condizioni sperimentali (es. 'baseline vs th_resp')
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
"

Effettivamente vengono create delle tuple di coppie di stringhe che corrispondono a quelle con cui dovrebbero esser create le sotto-sotto-chiavi delle coppie di condizioni sperimentali..

tuttavia, è giusto che iteri rispetto a 'condition_pairs', ma deve inserire un qualche controllo anche rispetto a questa cosa:

originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo

print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n") print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n") print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n") print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")

Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza, nel tuo codice, ho bisogno che

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, che nel caso di "condition_pairs" dovrebbe corrispondere ai primi 3 elementi della sua lista no, perché sarebbero 

[('baseline', 'th_resp'), 
    ('baseline', 'pt_resp'), 
    ('baseline', 'shared_resp'), 

è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare, che fa riferimento a questi altri elementi di 
"condition_pairs" che è creato nel loop ossia

('th_resp', 'pt_resp'), 
('th_resp', 'shared_resp'), 
('pt_resp', 'shared_resp')]

le labels andranno ovviamente riconvertite! Perché? 

Perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempio, in quel caso, le sue labels (che son originariamente codificate come '1' in 'new_subject_level_concatenations'!) diventeranno '0',

mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...

è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?dentro "# Crea tutte le combinazioni uniche di condizioni sperimentali (es. 'baseline vs th_resp')
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
    "

effettivamente vengono create delle tuple di coppie di stringhe che corrispondono a quelle con cui dovrebbero esser create le sotto-sotto-chiavi delle coppie di condizioni sperimentali..

tuttavia, è giusto che iteri rispetto a 'condition_pairs', ma deve inserire un qualche controllo anche rispetto a questa cosa:

originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo

print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n") print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n") print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n") print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")

Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza, nel tuo codice, ho bisogno che

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, che nel caso di "condition_pairs" dovrebbe corrispondere ai primi 3 elementi della sua lista no, perché sarebbero 

[('baseline', 'th_resp'), 
    ('baseline', 'pt_resp'), 
    ('baseline', 'shared_resp'), 

è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare, che fa riferimento a questi altri elementi di 
"condition_pairs" che è creato nel loop ossia

('th_resp', 'pt_resp'), 
('th_resp', 'shared_resp'), 
('pt_resp', 'shared_resp')]

le labels andranno ovviamente riconvertite! Perché? 

Perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempio, in quel caso, le sue labels (che son originariamente codificate come '1' in 'new_subject_level_concatenations'!) diventeranno '0',

mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...

è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?



##### Implementazione STEP - Concatenazione All Single Subject Spectrograms (TH) across Couples of Experimental Conditions

In [40]:
new_single_th_all_extracted_spectrograms_2D.keys()

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [41]:
new_single_th_all_extracted_spectrograms_2D['spectrograms_baseline_1'].keys()

dict_keys(['spectrograms', 'labels'])

In [42]:
type(new_single_th_all_extracted_spectrograms_2D['spectrograms_baseline_1'])

dict

In [43]:
print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_spectrograms_2D['spectrograms_baseline_1']['labels'], return_counts = True)}\n")
print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_spectrograms_2D['spectrograms_th_resp_1']['labels'], return_counts = True)}\n")
print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_spectrograms_2D['spectrograms_pt_resp_1']['labels'], return_counts = True)}\n")
print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_spectrograms_2D['spectrograms_shared_resp_1']['labels'], return_counts = True)}\n")

Baseline in TH_1:, (array(['0'], dtype='<U1'), array([44]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([43]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([47]))



In [44]:
new_single_th_all_extracted_spectrograms_2D['spectrograms_baseline_1'].keys()

dict_keys(['spectrograms', 'labels'])

In [45]:
'''DETAILED VERSION WITH COMPLICATED PRINTS

    CORREZIONE UFFICIALE PER SPETTROGRAMS
'''


import itertools
import numpy as np

# Definizione delle condizioni sperimentali
experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']

# Variabile per tenere traccia del soggetto corrente (per output facoltativo)
last_subject_key = None

# Dizionario per tenere traccia delle combinazioni già elaborate per ogni soggetto (evitare duplicati)
printed_combinations = {}

# Nuovo dizionario per memorizzare i risultati concatenati per coppia di condizioni per ogni soggetto
new_subject_level_concatenations_spectrograms_coupled_exp_th = {}

# Itera su tutte le chiavi del dizionario di partenza
for key in new_single_th_all_extracted_spectrograms_2D.keys():
    # Esempio di key: "spectrograms_baseline_1", "spectrograms_th_resp_1", etc.
    key_parts = key.split('_')
    subject_number = key_parts[-1] if key_parts[-1].isdigit() else None
    if subject_number is None:
        continue  # Salta eventuali chiavi non valide
    
    # Crea il nome del soggetto (es. "th_1")
    subject_key = f"th_{subject_number}"
    
    # Se cambiamo soggetto, stampiamo (facoltativo)
    if subject_key != last_subject_key:
        if last_subject_key is not None:
            print("\n" + "-" * 50 + f" END OF {last_subject_key.upper()} " + "-" * 50 + "\n")
        print(f"\nProcessing Subject: {subject_key}\n" + "=" * 80)
        printed_combinations[subject_key] = set()  # Inizializza il set per il soggetto corrente
    last_subject_key = subject_key

    # Inizializza la struttura per il soggetto se non esiste già
    if subject_key not in new_subject_level_concatenations_spectrograms_coupled_exp_th:
        new_subject_level_concatenations_spectrograms_coupled_exp_th[subject_key] = {}

    # Crea tutte le combinazioni uniche di condizioni sperimentali (es. "baseline_vs_th_resp")
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
    
    # Loop sulle coppie di condizioni
    for cond_1, cond_2 in condition_pairs:
        condition_pair_key = f"{cond_1}_vs_{cond_2}"
        if condition_pair_key in printed_combinations[subject_key]:
            continue  # Salta se già elaborata per questo soggetto
        
        print(f"\n\tCreation of Coupled Condition: \033[1m{condition_pair_key}\033[0m")
        printed_combinations[subject_key].add(condition_pair_key)
        
        # Estrai i dati e le etichette per la prima condizione
        data_cond_1 = new_single_th_all_extracted_spectrograms_2D.get(f"spectrograms_{cond_1}_{subject_number}", {}).get('spectrograms')
        labels_cond_1 = new_single_th_all_extracted_spectrograms_2D.get(f"spectrograms_{cond_1}_{subject_number}", {}).get('labels')
        
        # Estrai i dati e le etichette per la seconda condizione
        data_cond_2 = new_single_th_all_extracted_spectrograms_2D.get(f"spectrograms_{cond_2}_{subject_number}", {}).get('spectrograms')
        labels_cond_2 = new_single_th_all_extracted_spectrograms_2D.get(f"spectrograms_{cond_2}_{subject_number}", {}).get('labels')
        
        # Salta la coppia se uno dei dati non è presente
        if data_cond_1 is None or labels_cond_1 is None or data_cond_2 is None or labels_cond_2 is None:
            continue
        
        # Riassegna le etichette: tutti 0 per cond_1, tutti 1 per cond_2
        labels_cond_1 = np.zeros_like(labels_cond_1, dtype=int)
        labels_cond_2 = np.ones_like(labels_cond_2, dtype=int)
        
        # Concatenazione dei dati (verticale) e delle etichette (orizzontale)
        concatenated_data = np.concatenate((data_cond_1, data_cond_2), axis=0)
        concatenated_labels = np.concatenate((labels_cond_1, labels_cond_2), axis=0)
        
        # Salva il risultato per questa coppia nel dizionario del soggetto
        new_subject_level_concatenations_spectrograms_coupled_exp_th[subject_key][condition_pair_key] = {
            'data': concatenated_data,
            'labels': concatenated_labels
        }
        
        print(f"Condition pair '{condition_pair_key}' for subject {subject_key} => Data shape: {concatenated_data.shape}, Labels length: {len(concatenated_labels)}")



Processing Subject: th_1

	Creation of Coupled Condition: baseline_vs_th_resp
Condition pair 'baseline_vs_th_resp' for subject th_1 => Data shape: (84, 45, 61), Labels length: 84

	Creation of Coupled Condition: baseline_vs_pt_resp
Condition pair 'baseline_vs_pt_resp' for subject th_1 => Data shape: (87, 45, 61), Labels length: 87

	Creation of Coupled Condition: baseline_vs_shared_resp
Condition pair 'baseline_vs_shared_resp' for subject th_1 => Data shape: (91, 45, 61), Labels length: 91

	Creation of Coupled Condition: th_resp_vs_pt_resp
Condition pair 'th_resp_vs_pt_resp' for subject th_1 => Data shape: (83, 45, 61), Labels length: 83

	Creation of Coupled Condition: th_resp_vs_shared_resp
Condition pair 'th_resp_vs_shared_resp' for subject th_1 => Data shape: (87, 45, 61), Labels length: 87

	Creation of Coupled Condition: pt_resp_vs_shared_resp
Condition pair 'pt_resp_vs_shared_resp' for subject th_1 => Data shape: (90, 45, 61), Labels length: 90

-------------------------------

In [46]:
print(f"\t\t\t\t\033[1mStructure of new_subject_level_concatenations_spectrograms_coupled_exp_th\033[0m: \n")
print(f"\033[1mFirst Order Keys\033[0m: {new_subject_level_concatenations_spectrograms_coupled_exp_th.keys()}\n")
print(f"\033[1mSecond Order Keys\033[0m: {new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1'].keys()}\n")
print(f"\033[1mThird Order Keys\033[0m: \n{new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['baseline_vs_th_resp'].keys()}\n")

				Structure of new_subject_level_concatenations_spectrograms_coupled_exp_th: 

First Order Keys: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16', 'th_17', 'th_18', 'th_19', 'th_20'])

Second Order Keys: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

Third Order Keys: 
dict_keys(['data', 'labels'])



In [47]:
'''VERIFICO CHE LA CONCATENAZIONE SIA AVVENUTA CORRETTAMENTE!

    CORREZIONE UFFICIALE PER SPETTROGRAMS
'''

print("\tNOW, LET US SEE IF THE CONCATENATIONS RESPECT THE ORIGINAL SHAPES FOR EVERY COUPLED EXPERIMENTAL CONDITION!")
print("\tFOR THE 1°ST SUBJECT: CHECK IF THE SUM OF INDIVIDUAL EXP COND SHAPE MATCHES THE COUPLED COND CONCATENATION SHAPE:\n\n")

print("\033[1mINDIVIDUAL EXP COND SHAPE OF FIRST SUBJECT\033[0m:")

# Verifica delle dimensioni originali per le singole condizioni sperimentali
for cond in ['baseline', 'th_resp', 'pt_resp', 'shared_resp']:
    key = f'spectrograms_{cond}_1'
    if key in new_single_th_all_extracted_spectrograms_2D:
        unique_labels, counts = np.unique(new_single_th_all_extracted_spectrograms_2D[key]['labels'], return_counts=True)
        print(f"{cond.capitalize()} in TH_1: {unique_labels}, Counts: {counts}\n")
    else:
        print(f"Warning: {key} not found in new_single_th_all_extracted_spectrograms_2D\n")

# Seleziona il primo soggetto (ad esempio, 'th_1')
subject_key = 'th_1'

# Itera per ogni coppia di condizioni sperimentali direttamente (senza livelli)
for condition_pair_key, data_labels in new_subject_level_concatenations_spectrograms_coupled_exp_th.get(subject_key, {}).items():
    
    # Estrarre dati e labels dalla struttura corretta
    data = data_labels['data']
    labels = data_labels['labels']

    # Stampare il nome della coppia di condizioni e le loro dimensioni
    print(f"Condition Pair: \033[1m{condition_pair_key}\033[0m")
    
    if data is not None and labels is not None:
        print(f"  Data Shape: {data.shape}")
        print(f"  Labels Shape: {labels.shape}")
    else:
        print("  Missing data or labels!")

        

	NOW, LET US SEE IF THE CONCATENATIONS RESPECT THE ORIGINAL SHAPES FOR EVERY COUPLED EXPERIMENTAL CONDITION!
	FOR THE 1°ST SUBJECT: CHECK IF THE SUM OF INDIVIDUAL EXP COND SHAPE MATCHES THE COUPLED COND CONCATENATION SHAPE:


INDIVIDUAL EXP COND SHAPE OF FIRST SUBJECT:
Baseline in TH_1: ['0'], Counts: [44]

Th_resp in TH_1: ['1'], Counts: [40]

Pt_resp in TH_1: ['2'], Counts: [43]

Shared_resp in TH_1: ['3'], Counts: [47]

Condition Pair: baseline_vs_th_resp
  Data Shape: (84, 45, 61)
  Labels Shape: (84,)
Condition Pair: baseline_vs_pt_resp
  Data Shape: (87, 45, 61)
  Labels Shape: (87,)
Condition Pair: baseline_vs_shared_resp
  Data Shape: (91, 45, 61)
  Labels Shape: (91,)
Condition Pair: th_resp_vs_pt_resp
  Data Shape: (83, 45, 61)
  Labels Shape: (83,)
Condition Pair: th_resp_vs_shared_resp
  Data Shape: (87, 45, 61)
  Labels Shape: (87,)
Condition Pair: pt_resp_vs_shared_resp
  Data Shape: (90, 45, 61)
  Labels Shape: (90,)


In [48]:
print(np.unique(new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['baseline_vs_th_resp']['labels'], return_counts = True))
print(np.unique(new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['th_resp_vs_shared_resp']['labels'], return_counts = True))

(array([0, 1]), array([44, 40]))
(array([0, 1]), array([40, 47]))


In [49]:
print(f"\t\t\t\033[1mBASELINE_VS_TH_RESP\033[0m\n")
print(new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['baseline_vs_th_resp']['labels'][:51])
print(new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['baseline_vs_th_resp']['labels'][51:])
print()
print()
print(f"\t\t\t\033[1mTH_RESP_VS_SHARED_RESP\033[0m\n")
print(new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['th_resp_vs_shared_resp']['labels'][:40])
print(new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['th_resp_vs_shared_resp']['labels'][40:])


			BASELINE_VS_TH_RESP

[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 1 1 1 1 1 1 1]
[1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]


			TH_RESP_VS_SHARED_RESP

[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0]
[1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
 1 1 1 1 1 1 1 1 1 1]


##### STEP - Salvataggio Dataset di All Single Therapists EEG Data Spectrograms across Couples of Experimental Conditions

In [50]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [51]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_NF '''
import pickle

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_subject_level_concatenations_spectrograms_coupled_exp_th.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_spectrograms_coupled_exp_th, f)

#### **Concatenazione** **ALL** Single Subject **Spectrograms (TH)** per **Coppie di Condizioni Sperimentali INSIEME**

In [52]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_NF '''

import pickle

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_subject_level_concatenations_spectrograms_coupled_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_spectrograms_coupled_exp_th = pickle.load(f)

In [53]:
#new_subject_level_concatenations_spectrograms_coupled_exp_th.keys()
#new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1'].keys()
#new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['theta'].keys()
#new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()
#np.unique(new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['labels'], return_counts = True)

In [54]:
np.unique(new_subject_level_concatenations_spectrograms_coupled_exp_th['th_1']['baseline_vs_th_resp']['labels'], return_counts = True)

(array([0, 1]), array([44, 40]))

In [55]:
'''CODICE UFFICIALE CON MODIFICHE A SPETTROGRAMMI'''


import numpy as np

def concatenate_all_subjects_coupled_spectrogram_conditions_th(data_structure, conditions):
    
    """
    Concatena globalmente i dati e le etichette per ogni coppia di condizioni sperimentali
    a partire dalla struttura 'new_subject_level_concatenations_spectrograms_coupled_exp_th'.
    I dati di ogni soggetto (già raggruppati per coppia di condizioni) vengono ulteriormente 
    concatenati per ottenere un unico array globale per ogni coppia.
    
    Parameters:
        data_structure (dict): Struttura dati con chiavi per soggetto (es. 'th_1', 'th_2', ...)
                               e, per ciascun soggetto, chiavi per ciascuna coppia di condizioni sperimentali.
        condition_pairs (list): Lista di coppie di condizioni sperimentali (es. 'baseline_vs_th_resp', ...)
        
    Returns:
        dict: Un dizionario globale in cui ogni chiave è una coppia di condizioni e il valore
              è un dizionario con 'data' e 'labels' concatenati globalmente (da tutti i soggetti).
    """
        
    # Dizionario per contenere i dati concatenati di tutti i soggetti
    all_subj_data_by_coupled_cond = {}

    # Itera su ogni coppia di condizioni sperimentali
    for condition_pair in conditions:

        #Dizionari per raccogliere dati e labels ordinati per ogni coppia di condizioni sperimentali
        # che è dinamico, per ogni coppia di condizioni sperimentali 
        #(quindi si ricreeranno passando alla condizione sperimentale successiva!)

        data_by_label = {}
        labels_by_label = {}
        shape_labels_per_subject = {0: [], 1: []}  # Inizializza il dizionario per 0 e 1

        # Itera su tutti i soggetti
        # In questo caso, itera sulle chiavi di ogni soggetto

        # Quindi prenderà, per la relativa coppia di condizioni sperimentali di ogni soggetto,
        # i dati e le labels di quel soggetto, per quella relativa coppia di condizioni sperimentali

        for subject_key in data_structure.keys():

            # Controlla se il livello di ricostruzione esiste per il soggetto
            if condition_pair not in data_structure[subject_key]:
                continue

            # Qui estrae i dati e le labels per questa condizione sperimentale di quel soggettio lì
            subject_data = data_structure[subject_key][condition_pair]['data']
            subject_labels = data_structure[subject_key][condition_pair]['labels']

            # Trova le etichette uniche e gli indici corrispondenti per quella coppia di condizioni sperimentali lì,
            # Ossia, potrà trovare gli 0 e gli 1 

            unique_labels = np.unique(subject_labels)

            #A quel punto, per ognuna delle due labels trovate per quella coppia di condizioni sperimentali lì
            #Che saranno sempre o 0 o 1

            for label in unique_labels:

                # Trova gli indici dei dati corrispondenti a questa etichetta
                # Una volta per lo 0 ed una volta per l' 1

                label_indices = np.where(subject_labels == label)[0]

                # A quel punto, estrae i dati e le labels per questi indici
                # Una volta per lo 0 ed una volta per l' 1

                data_for_label = subject_data[label_indices]
                labels_for_label = subject_labels[label_indices]

                # A quel punto, per ogni soggetto, per ogni condzione sperimentale, 
                # per quelle due labels là (sempre presenti, per ogni coppia di condizioni sperimentali)
                # Una volta per lo 0 ed una volta per l' 1

                #Andrà a creare per ogni etichetta, una chiave che si chiamerà 
                #o 0 od 1 (inizialmente, vuoto -> perché deve esser inizializzato)
                #E poi, dopo, ci appenderà le labels 
                 # Una volta per lo 0 ed una volta per l' 1
                #  Di quel soggetto per quella coppia di condizioni sperimentali iterate a quel momento

                #Aggiunge ai dizionari globali, creando la chiave se non esiste
                if label not in data_by_label:
                    data_by_label[label] = []
                    labels_by_label[label] = []

                data_by_label[label].append(data_for_label)
                labels_by_label[label].append(labels_for_label)

                # **Salva la shape delle etichette per il soggetto corrente**
                shape_labels_per_subject[label].append(labels_for_label.shape[0]) # Aggiungi solo la dimensione (numero di etichette)

                '''PRINT PER CHECK LABELS DI OGNI SOGGETTO PER OGNI COPPIA DI CONDIZIONE CONDIZIONI SPERIMENTALI''' 
                #print(f"Soggetto: \033[1m{subject_key}\033[0m, Livello: \033[1m{reconstruction_level}\033[0m, Condizione: \033[1m{condition_pair}\033[0m, "
                #      f"Etichetta: \033[1m{label}\033[0m, Shape: \033[1m{labels_for_label.shape[0]}\033[0m")

                # **Aggiungi un print di controllo per ogni soggetto**
                #print(f"Soggetto: \033[1m{subject_key}\033[1m, Livello: {reconstruction_level}, Condizione: {condition_pair}, Etichetta: {label}, Shape: {labels_for_label.shape[0]}")

            
        #*** *** *** *** *** *** *** *** *** *** *** *** *** *** ***

        # Dopodiché, vado a creare invece i dizionari che conterranno
        # Le concatenazioni, di dati e labels corrispondenti, di tutti i soggetti per cui l'etichetta era 
        # o 0 od 1 

        # Di conseguenza, qui dentro dovrei avere, per ogni coppia di condizioni sperimentali
        # Tutti gli 0 ed 1 (ed i relativi dati corrispondenti)
        # di tutti i soggetti, ma concatenati

        concatenated_data_by_label = {}
        concatenated_labels_by_label = {}

        #for label in data_by_label.keys():
        #    if len(data_by_label[label]) > 0:  # Evita errori di concatenazione
        #        concatenated_data_by_label[label] = np.vstack(data_by_label[label])
        #        concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
            
        for label in data_by_label.keys():
            concatenated_data_by_label[label] = np.vstack(data_by_label[label])
            concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])

            # **Calcolare la shape totale delle etichette**
            #total_labels_0 = np.sum(1 for subject_labels in labels_by_label[label] if 0 in subject_labels)
            #total_labels_1 = np.sum(1 for subject_labels in labels_by_label[label] if 1 in subject_labels)
            #total_labels = total_labels_0 + total_labels_1

            # **Determinare gli indici delle etichette 0 e 1 nell'array finale**

            # Gli indici delle etichette 0
            indices_labels_0 = np.where(concatenated_labels_by_label[label] == 0)[0]

            # Gli indici delle etichette 1
            indices_labels_1 = np.where(concatenated_labels_by_label[label] == 1)[0]

            # Indici iniziale e finale per le etichette 0 e 1
            start_idx_0 = indices_labels_0[0] if len(indices_labels_0) > 0 else None
            end_idx_0 = indices_labels_0[-1] if len(indices_labels_0) > 0 else None
            start_idx_1 = indices_labels_1[0] if len(indices_labels_1) > 0 else None
            end_idx_1 = indices_labels_1[-1] if len(indices_labels_1) > 0 else None


            # **Print finale per verificare la concatenazione per ogni label**
            #print(f"\nCondizione: \033[1m{condition_pair}\033[0m, Etichetta: {label}")
            #print(f"  - Shape dei dati concatenati per \033[1m{label}\033[0m: {concatenated_data_by_label[label].shape}")
            #print(f"  - Shape delle etichette concatenate per \033[1m{label}\033[0m: {concatenated_labels_by_label[label].shape}")

            # **Stampa la lista delle shapes delle etichette per ogni soggetto per questa etichetta**
            #print(f"\n  - Shape delle etichette per soggetto (per etichetta {label}): {shape_labels_per_subject[label]}\n")


            # **Stampa il conteggio totale delle etichette**
            #print(f"\n  - Totale delle etichette 0: {total_labels_0}")
            #print(f"  - Totale delle etichette 1: {total_labels_1}")
            #print(f"  - Totale delle etichette per la condizione: {total_labels}\n")

            # **Stampa gli indici per le etichette 0 e 1**
            # **OSSIA --> Stampa gli indici per l'etichetta corrente**

            #if label == 0:
            #    print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #else:
            #    print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}\n")


            #print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}")


        #ARRIVATI FINO A QUI, abbiamo che siccome stiamo iterando prima per tutti gli 0 e poi per tutti gli 1
        #Significa che, assumendo che siamo dentro 'baseline_vs_th_resp' e che 

        #'baseline' sia rappresentato dalle etichette 0
        #'th_resp' sia rappresentato dalle etichette 1

        #Al PRIMO ciclo avrò che:

        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'baseline' per 'baseline_vs_th_resp'di tutti i soggetti)

        #Al SECONDO ciclo avrò che:

        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)

        #Quindi mi manca ancora 

        #A) CONCATENARE I DATI:

        #1)prima tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 

        #CON

        #2)tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)

        #che verrà fatto dentro all_data (che è anch'esso una variabile dinamica!)

        #B) CONCATENARE LE LABELS:

        #1)prima tutti le labels (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 

        #CON

        #2)tutti le labels (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)

        #che verrà fatto dentro all_labels (che è anch'esso una variabile dinamica!)

        # Liste per raccogliere dati e labels di tutte le etichette

        # Qui dentro, invece, dov con

        all_data = []
        all_labels = []

        for label in concatenated_data_by_label.keys():
            all_data.append(concatenated_data_by_label[label])
            all_labels.append(concatenated_labels_by_label[label])

        #Alla fine, qui dentro avrò che, PER OGNI COPPIA DI CONDIZIONI SPERIMENTALI


        #'final_data' dovrebbe avere 
            #- prima tutti i dati di tutti i soggetti associati all'etichetta 0 
            #- e poi tutti i dati di tutti i soggetti associati all'etichetta 1

        #'final_labels' dovrebbe avere 
            #- prima tutte le labels di tutti i soggetti associati all'etichetta 0
            #- e poi tutte tutte le labels di tutti soggetti associati all'etichetta 1...

        if all_data:  # Evita errori di concatenazione se non ci sono dati
            final_data = np.vstack(all_data)
            final_labels = np.hstack(all_labels)

            all_subj_data_by_coupled_cond[condition_pair] = {
                'data': final_data,
                'labels': final_labels
            }
            
    return all_subj_data_by_coupled_cond


In [56]:
# Parametri
conditions = ['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp',
              'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp']

# Chiamata alla funzione, qui definisco a mano il nome della variabile (i.e., 
new_all_th_concat_spectrograms_coupled_exp = concatenate_all_subjects_coupled_spectrogram_conditions_th(
    data_structure = new_subject_level_concatenations_spectrograms_coupled_exp_th,
    conditions = conditions
)

print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")


for condition_pair, value in new_all_th_concat_spectrograms_coupled_exp.items():
    labels = value['labels']
    unique_labels = np.unique(labels)
    total_labels = 0

    print(f"\nCondizione: \033[1m{condition_pair}\033[0m")
    for label in unique_labels:
        label_indices = np.where(labels == label)[0]
        start_idx = label_indices[0] if len(label_indices) > 0 else None
        end_idx = label_indices[-1] if len(label_indices) > 0 else None
        total_labels += len(label_indices)

        print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m "
              f"(Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

    print(f"Totale etichette (0 e 1): \033[1m{total_labels}\033[0m\n")


Intervalli di indici per ciascuna etichetta nei sotto-dizionari:


Condizione: baseline_vs_th_resp
  Etichetta 0: Indici 0-1124 (Totale Etichette: 1125)
  Etichetta 1: Indici 1125-1916 (Totale Etichette: 792)
Totale etichette (0 e 1): 1917


Condizione: baseline_vs_pt_resp
  Etichetta 0: Indici 0-1124 (Totale Etichette: 1125)
  Etichetta 1: Indici 1125-1918 (Totale Etichette: 794)
Totale etichette (0 e 1): 1919


Condizione: baseline_vs_shared_resp
  Etichetta 0: Indici 0-1124 (Totale Etichette: 1125)
  Etichetta 1: Indici 1125-2265 (Totale Etichette: 1141)
Totale etichette (0 e 1): 2266


Condizione: th_resp_vs_pt_resp
  Etichetta 0: Indici 0-791 (Totale Etichette: 792)
  Etichetta 1: Indici 792-1585 (Totale Etichette: 794)
Totale etichette (0 e 1): 1586


Condizione: th_resp_vs_shared_resp
  Etichetta 0: Indici 0-791 (Totale Etichette: 792)
  Etichetta 1: Indici 792-1932 (Totale Etichette: 1141)
Totale etichette (0 e 1): 1933


Condizione: pt_resp_vs_shared_resp
  Etichetta 0: Indic

##### STEP - Salvataggio Dataset di **All Single Therapists** EEG Data Spectrograms across **Couples of Experimental Conditions** INSIEME

In [57]:
pwd

'/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45'

In [58]:
cd ..

/home/stefano/Interrogait


In [59]:
cd New_Plots_Sliding_Estimator_MNE_1_45/

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [60]:
'''PATH  --> cd Unfamiliar_Wavelet_Reconstructions'''

import pickle
import os
   
#base_path = '/home/stefano/Interrogait/all_datas/Unfamiliar_Spectrograms'

# Controlla se la cartella esiste, altrimenti la crea
#if not os.path.exists(base_path):
#    os.makedirs(base_path)

# Salvare l'intero dizionario annidato con pickle
#with open(f'{base_path}/new_all_th_concat_spectrograms_coupled_exp.pkl', 'wb') as f:
#    pickle.dump(new_all_th_concat_spectrograms_coupled_exp, f)
    


#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'


fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Controlla se la cartella esiste, altrimenti la crea
if not os.path.exists(fam_path):
    os.makedirs(fam_path)

# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_all_th_concat_spectrograms_coupled_exp.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_spectrograms_coupled_exp, f)

#### **Concatenazione** All **SINGLE** Subject **Spectrograms (TH)** per **Triplets of Experimental Conditions**

##### Procedura

Per calcolare quante possibili triplette (combinazioni di 3 condizioni sperimentali) si possono formare da un insieme di 4 condizioni, utilizziamo il concetto di combinazioni senza ripetizione. La formula per il numero di combinazioni è:

C(n,k)=  k!⋅(n−k)! / n!

Dove:

- n è il numero totale di elementi nell'insieme (n = 4 in questo caso)
- k è il numero di elementi scelti (k = 3)


**Calcoliamo**:

C(4,3)= 4!/ 3⋅(4−3)! = 4⋅3⋅2⋅1 / (3⋅2⋅1)⋅1 = 4 

**Risultato**

Ci sono 4 possibili triplette che si possono formare dalle 4 condizioni sperimentali.

**Elenco delle Triplette**

Se vogliamo enumerarle:

['baseline', 'th_resp', 'pt_resp']
['baseline', 'th_resp', 'shared_resp']
['baseline', 'pt_resp', 'shared_resp']
['th_resp', 'pt_resp', 'shared_resp']

Queste sono tutte le combinazioni possibili


##### Implementazione

In [61]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [62]:
cd ..

/home/stefano/Interrogait


In [63]:
cd New_Plots_Sliding_Estimator_MNE_1_45/

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [64]:
import pickle
import numpy as np

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Unfamiliar_Spectrograms_channels_frequencies/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_single_th_all_extracted_spectrograms_2D.pkl', 'rb') as f:
    new_single_th_all_extracted_spectrograms_2D = pickle.load(f)

In [65]:
print(new_single_th_all_extracted_spectrograms_2D.keys())
print()
print(new_single_th_all_extracted_spectrograms_2D['spectrograms_baseline_1'].keys())

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [66]:
'''NEW IMPLEMENTATION'''

import itertools
import numpy as np

# Definisci le condizioni sperimentali
experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']

# Nuovo dizionario di output per le triplette
new_subject_level_concatenations_spectrograms_triplets_exp_th = {}

'''

PROBLEMA:

Nel codice che ho fornito,
sto creando delle chiavi per i soggetti come th_1, th_2, etc.,
basate sui numeri estratti dalle chiavi di new_single_th_all_extracted_spectrograms_2D. 

Tuttavia, l'ordinamento che sto usando potrebbe non essere numericamente corretto... 

Quando si crea una lista di numeri con la funzione sorted(set(...)), 
Python li ordina lessicograficamente come STRINGHE (STR), quindi th_10 verrà messo prima di th_2 
(perché la stringa '10' viene considerata più piccola di '2').


# Estrai i numeri unici dei soggetti dalle chiavi di new_single_th_all_extracted_spectrograms_2D
#CON ORDINAMENTO LESSICOGRAFICO DI STRINGHE
#unique_subject_numbers = sorted(set(key.split('_')[-1] for key in new_single_th_all_extracted_spectrograms_2D.keys() 
#                                     if key.split('_')[-1].isdigit()))


SOLUZIONE:

Si può risolvere questo problema modificando il modo in cui ordini i numeri,
trattandoli come NUMERI INTERI (INT), non come stringhe.
A tal fine, puoi usare un approccio simile a quello che ti ho suggerito prima,
ovvero estrarre il numero del soggetto e ordinarlo correttamente come intero. Invece di utilizzare sorted(set(...))
'''

#CON ORDINAMENTO BASATO SUGLI INTEGER

unique_subject_numbers = sorted(
    set(int(key.split('_')[-1]) for key in new_single_th_all_extracted_spectrograms_2D.keys() if key.split('_')[-1].isdigit())
)

# Itera su ogni soggetto (per esempio, "1", "2", "3", ecc.)
for subject in unique_subject_numbers:
    subject_key = f"th_{subject}"
    new_subject_level_concatenations_spectrograms_triplets_exp_th[subject_key] = {}
    
    print(f"\nProcessing Subject: {subject_key}\n" + "=" * 80)
    
    # Crea tutte le combinazioni uniche di triplette di condizioni sperimentali
    condition_triplets = list(itertools.combinations(experimental_conditions, 3))
    
    # Loop su ogni triplette di condizioni
    for cond1, cond2, cond3 in condition_triplets:
        condition_triplet_key = f"{cond1}_vs_{cond2}_vs_{cond3}"
        print(f"\n\tCreation of Triplet Condition: \033[1m{condition_triplet_key}\033[0m")
        
        # Costruisci i nomi delle chiavi per ciascuna condizione per questo soggetto
        key_cond1 = f"spectrograms_{cond1}_{subject}"
        key_cond2 = f"spectrograms_{cond2}_{subject}"
        key_cond3 = f"spectrograms_{cond3}_{subject}"
        
        # Verifica che i dati per tutte le condizioni siano presenti
        if key_cond1 not in new_single_th_all_extracted_spectrograms_2D or \
           key_cond2 not in new_single_th_all_extracted_spectrograms_2D or \
           key_cond3 not in new_single_th_all_extracted_spectrograms_2D:
            print(f"\tMissing data for one of the conditions in triplet {condition_triplet_key} for {subject_key}. Skipping.")
            continue
        
        # Estrai i dati e le etichette per ciascuna condizione
        data_cond1 = new_single_th_all_extracted_spectrograms_2D[key_cond1]['spectrograms']
        labels_cond1 = new_single_th_all_extracted_spectrograms_2D[key_cond1]['labels']
        
        data_cond2 = new_single_th_all_extracted_spectrograms_2D[key_cond2]['spectrograms']
        labels_cond2 = new_single_th_all_extracted_spectrograms_2D[key_cond2]['labels']
        
        data_cond3 = new_single_th_all_extracted_spectrograms_2D[key_cond3]['spectrograms']
        labels_cond3 = new_single_th_all_extracted_spectrograms_2D[key_cond3]['labels']
        
        # Assegna etichette fisse per ciascuna condizione (0, 1, 2)
        labels_cond1 = np.zeros(len(labels_cond1), dtype=int)
        labels_cond2 = np.ones(len(labels_cond2), dtype=int)
        labels_cond3 = np.full(len(labels_cond3), 2, dtype=int)
        
        # Concatenazione dei dati (verticale) e delle etichette (orizzontale)
        concatenated_data = np.vstack((data_cond1, data_cond2, data_cond3))
        concatenated_labels = np.hstack((labels_cond1, labels_cond2, labels_cond3))
        
        # Salva il risultato per questa triplette nel dizionario del soggetto
        new_subject_level_concatenations_spectrograms_triplets_exp_th[subject_key][condition_triplet_key] = {
            'data': concatenated_data,
            'labels': concatenated_labels
        }
        
        print(f"\n\tExtracted Experimental Conditions: "
              f"\n\t\033[1m{key_cond1}\033[0m shape: \t{data_cond1.shape}, \n\t\033[1m{key_cond2}\033[0m shape: {data_cond2.shape}, \n\t\033[1m{key_cond3}\033[0m shape: {data_cond3.shape}")
        print(f"\n\tConcatenated of Triplet Conditions Data shape: {concatenated_data.shape}, Concatenated labels shape: {concatenated_labels.shape}")


Processing Subject: th_1

	Creation of Triplet Condition: baseline_vs_th_resp_vs_pt_resp

	Extracted Experimental Conditions: 
	spectrograms_baseline_1 shape: 	(51, 45, 61), 
	spectrograms_th_resp_1 shape: (40, 45, 61), 
	spectrograms_pt_resp_1 shape: (40, 45, 61)

	Concatenated of Triplet Conditions Data shape: (131, 45, 61), Concatenated labels shape: (131,)

	Creation of Triplet Condition: baseline_vs_th_resp_vs_shared_resp

	Extracted Experimental Conditions: 
	spectrograms_baseline_1 shape: 	(51, 45, 61), 
	spectrograms_th_resp_1 shape: (40, 45, 61), 
	spectrograms_shared_resp_1 shape: (56, 45, 61)

	Concatenated of Triplet Conditions Data shape: (147, 45, 61), Concatenated labels shape: (147,)

	Creation of Triplet Condition: baseline_vs_pt_resp_vs_shared_resp

	Extracted Experimental Conditions: 
	spectrograms_baseline_1 shape: 	(51, 45, 61), 
	spectrograms_pt_resp_1 shape: (40, 45, 61), 
	spectrograms_shared_resp_1 shape: (56, 45, 61)

	Concatenated of Triplet Conditions Data 

In [67]:
'''CHECK ORDINAMENTO CORRETTO DATI E LABELS NEW VERSION'''

import numpy as np

# Itera su ogni soggetto nel dizionario delle triplette
print("\n\033[1mIndicizzazione dei dati e delle etichette per ogni sotto-tripletta di condizioni sperimentali:\033[0m\n")

for subject_key, triplets_data in new_subject_level_concatenations_spectrograms_triplets_exp_th.items():
    print(f"\nSoggetto: \033[1m{subject_key}\033[0m")
    print("=" * 80)

    for triplet_key, triplet_data in triplets_data.items():
        print(f"\nTripletta: \033[1m{triplet_key}\033[0m")
        
        # Estrai i dati e le etichette
        concatenated_data = triplet_data['data']
        concatenated_labels = triplet_data['labels']
        
        # Conta le etichette uniche
        unique_labels = np.unique(concatenated_labels)
        
        # Variabile per il conteggio totale
        total_samples = 0
        
        for label in unique_labels:
            # Trova gli indici corrispondenti a questa etichetta
            label_indices = np.where(concatenated_labels == label)[0]
            
            # Determina l'intervallo di indici
            start_idx = label_indices[0]
            end_idx = label_indices[-1]
            
            # Aggiungi il numero di campioni al totale
            total_samples += len(label_indices)
            
            # Stampa le informazioni sull'etichetta
            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m (Totale: {len(label_indices)})")
        
        # Verifica il totale dei campioni
        print(f"\nTotale campioni per la triplette \033[1m{triplet_key}\033[0m: \033[1m{total_samples}\033[0m")
        print("-" * 80)



Indicizzazione dei dati e delle etichette per ogni sotto-tripletta di condizioni sperimentali:


Soggetto: th_1

Tripletta: baseline_vs_th_resp_vs_pt_resp
  Etichetta 0: Indici 0-50 (Totale: 51)
  Etichetta 1: Indici 51-90 (Totale: 40)
  Etichetta 2: Indici 91-130 (Totale: 40)

Totale campioni per la triplette baseline_vs_th_resp_vs_pt_resp: 131
--------------------------------------------------------------------------------

Tripletta: baseline_vs_th_resp_vs_shared_resp
  Etichetta 0: Indici 0-50 (Totale: 51)
  Etichetta 1: Indici 51-90 (Totale: 40)
  Etichetta 2: Indici 91-146 (Totale: 56)

Totale campioni per la triplette baseline_vs_th_resp_vs_shared_resp: 147
--------------------------------------------------------------------------------

Tripletta: baseline_vs_pt_resp_vs_shared_resp
  Etichetta 0: Indici 0-50 (Totale: 51)
  Etichetta 1: Indici 51-90 (Totale: 40)
  Etichetta 2: Indici 91-146 (Totale: 56)

Totale campioni per la triplette baseline_vs_pt_resp_vs_shared_resp: 147
-

In [68]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [69]:
'''PER SALVARE STRUTTURA DATI E LABEL OGNI SOGGETTO NON ANCORA CONCATENATI TRA DI LORO

PS: viene comunque già salvato in  --> new_subject_level_concatenations_triplets_exp_th_1_45 '''

import pickle

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Salva il dizionario th_data_dict in un file pkl
with open(f'{fam_path}/new_subject_level_concatenations_spectrograms_triplets_exp_th.pkl', 'wb') as file:
    pickle.dump(new_subject_level_concatenations_spectrograms_triplets_exp_th, file)


#### **Concatenazione All** Single **Subject Spectrograms (TH)** per  **Triplets of Experimental Conditions INSIEME**



In [70]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_subject_level_concatenations_spectrograms_triplets_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_spectrograms_triplets_exp_th = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_subject_level_concatenations_triplets_exp_th_1_45.pkl', 'rb') as f:
    new_subject_level_concatenations_triplets_exp_th_1_45 = pickle.load(f)
    

In [71]:
new_subject_level_concatenations_spectrograms_triplets_exp_th['th_1'].keys()

dict_keys(['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp', 'baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp'])

In [72]:
new_subject_level_concatenations_spectrograms_triplets_exp_th['th_1']['baseline_vs_th_resp_vs_pt_resp'].keys()

dict_keys(['data', 'labels'])

In [73]:
# Itera attraverso ogni soggetto nel dizionario
for i, subject_data in new_subject_level_concatenations_spectrograms_triplets_exp_th.items():
    print(f"Soggetto {i}:")
    print("Chiavi presenti:", list(subject_data.keys()))
    print("-" * 50)

Soggetto th_1:
Chiavi presenti: ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp', 'baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']
--------------------------------------------------
Soggetto th_2:
Chiavi presenti: ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp', 'baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']
--------------------------------------------------
Soggetto th_3:
Chiavi presenti: ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp', 'baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']
--------------------------------------------------
Soggetto th_4:
Chiavi presenti: ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp', 'baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']
--------------------------------------------------
Soggetto th_5:
Chiavi presenti: ['baseline_vs_th_resp_vs_pt_resp', 'baseline

In [74]:
#def concatenate_all_single_subj_spectrograms_tripled_experimental_conditions_th(data_structure, conditions, prefix, suffix):

def concatenate_all_single_subj_spectrograms_tripled_experimental_conditions_th(data_structure, conditions, prefix):
    
    """
    Concatena i dati e le etichette per ogni condizione sperimentale da una struttura dati con un livello in più,
    ordinandoli anche per etichetta.

    Parameters:
        data_structure (dict): La struttura dati di input che contiene i dati per soggetti e condizioni.
        conditions (list): Le condizioni sperimentali (chiavi del secondo livello) da processare.
        prefix (str): Il prefisso del nome dinamico del dizionario.
        #suffix (str): Il suffisso del nome dinamico del dizionario.

    Returns:
        dict: Un dizionario contenente i nuovi dizionari con i dati concatenati e le etichette per ogni condizione.
    """
    
    #Questo conterrà i dati complessivi di tutti i soggetti per ogni coppia di condizioni sperimentali
    all_subj_data_by_coupled_cond = {}

    # Itera su ogni condizione sperimentale
    for condition_triplet in conditions:
        
        # Dizionari per raccogliere dati e labels ordinati per ogni coppia di condizioni sperimentali
        # che è dinamico, per ogni coppia di condizioni sperimentali 
        
        #(quindi si ricreeranno passando alla condizione sperimentale successiva!)
        
        
        #print(f"Creo dizionari di dati e labels per la condizione:")
        #print(f"\n{condition_triplet}")
        data_by_label = {}
        labels_by_label = {}
        
        
        # Lista temporanea per salvare la shape delle etichette per ogni soggetto per ogni etichetta iterata
        
        '''
        Per ogni condizione sperimentale, per ognuna delle 2 labels, 
        la shape delle etichette per ogni soggetto, 

        e me le salvi dentro una lista temporanea, che salva in formato la shape (solo il valore numerico) di ogni soggetto 
        per l'etichette iterata per quella condizione sperimentale là.

        poi, a questo livello dei print 

         # **Print finale per verificare la concatenazione per ogni label**
            print(f"Condizione: {condition_triplet}, Etichetta: {label}")
            print(f"  - Shape dei dati concatenati per {label}: {concatenated_data_by_label[label].shape}")
            print(f"  - Shape delle etichette concatenate per {label}: {concatenated_labels_by_label[label].shape}")

        vorrei che mi stampassi anche questa lista alla fine del print, di modo che possa vedere visivamente subito il numero di labels di ogni soggetto associate a quella labels iterata là così da vedere se il conteggio corrisponde visivamente al totale salvate dentro 

        "concatenated_data_by_label[label]"
        '''
        
        shape_labels_per_subject = {0: [], 1: [], 2: []}  # Inizializza un dizionario per le etichette 0 e 1


        # Itera su tutti i soggetti
        # In questo caso, itera sulle chiavi di ogni soggetto
        
        # Quindi prenderà, per la relativa coppia di condizioni sperimentali di ogni soggetto,
        # i dati e le labels di quel soggetto, per quella relativa coppia di condizioni sperimentali
        
        for subject_key in data_structure.keys():
            
            #print(subject_key)
            #print(data_structure.keys())
            
            # Qui estrae i dati e le labels per questa condizione sperimentale di quel soggettio lì
            subject_data = data_structure[subject_key][condition_triplet]['data']
            subject_labels = data_structure[subject_key][condition_triplet]['labels']

            # Trova le etichette uniche e gli indici corrispondenti per quella coppia di condizioni sperimentali lì,
            # Ossia, potrà trovare gli 0 e gli 1 
            
            unique_labels = np.unique(subject_labels)
        
            #A quel punto, per ognuna delle due labels trovate per quella coppia di condizioni sperimentali lì
            #Che saranno sempre o 0 o 1 
            
            for label in unique_labels:
                
                # Trova gli indici dei dati corrispondenti a questa etichetta
                # Una volta per lo 0 ed una volta per l' 1
                
                label_indices = np.where(subject_labels == label)[0]

                # A quel punto, estrae i dati e le labels per questi indici
                # Una volta per lo 0 ed una volta per l' 1
                
                data_for_label = subject_data[label_indices]
                labels_for_label = subject_labels[label_indices]

                # A quel punto, per ogni soggetto, per ogni condzione sperimentale, 
                # per quelle due labels là (sempre presenti, per ogni coppia di condizioni sperimentali)
                # Una volta per lo 0 ed una volta per l' 1
                
                #Andrà a creare per ogni etichetta, una chiave che si chiamerà 
                #o 0 od 1 (inizialmente, vuoto -> perché deve esser inizializzato)
                #E poi, dopo, ci appenderà le labels 
                 # Una volta per lo 0 ed una volta per l' 1
                #  Di quel soggetto per quella coppia di condizioni sperimentali iterate a quel momento
                
                #Aggiunge ai dizionari globali, creando la chiave se non esiste
                if label not in data_by_label:
                    data_by_label[label] = []
                    labels_by_label[label] = []

                data_by_label[label].append(data_for_label)
                labels_by_label[label].append(labels_for_label)
                
                 # **Salva la shape delle etichette per il soggetto corrente**
                shape_labels_per_subject[label].append(labels_for_label.shape[0])  # Aggiungi solo la dimensione (numero di etichette)

        
                # **Aggiungi un print di controllo per ogni soggetto**
                print(f"Soggetto: \033[1m{subject_key}\033[0m, Condizione: \033[1m{condition_triplet}\033[0m, Etichetta: \033[1m{label}\033[0m, Shape: \033[1m{labels_for_label.shape[0]}\033[0m")
                #print(f"  - Numero di \033[1mdati\033[0m per {label}: {data_for_label.shape[0]}")
                #print(f"  - Numero di \033[1metichette\033[0m per {label}: {labels_for_label.shape[0]}")
                
                    
        # Dopodiché, vado a creare invece i dizionari che conterranno
        # Le concatenazioni, di dati e labels corrispondenti, di tutti i soggetti per cui l'etichetta era 
        # o 0 od 1 
        
        # Di conseguenza, qui dentro dovrei avere, per ogni coppia di condizioni sperimentali
        # Tutti gli 0 ed 1 (ed i relativi dati corrispondenti)
        # di tutti i soggetti, ma concatenati
        
        
        concatenated_data_by_label = {}
        concatenated_labels_by_label = {}

        for label in data_by_label.keys():
            concatenated_data_by_label[label] = np.vstack(data_by_label[label])
            concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
            
            # **Calcolare la shape totale delle etichette**
            #total_labels_0 = np.sum(1 for subject_labels in labels_by_label[label] if 0 in subject_labels)
            #total_labels_1 = np.sum(1 for subject_labels in labels_by_label[label] if 1 in subject_labels)
            #total_labels = total_labels_0 + total_labels_1

            # **Determinare gli indici delle etichette 0 e 1 nell'array finale**
            
            # Gli indici delle etichette 0
            indices_labels_0 = np.where(concatenated_labels_by_label[label] == 0)[0]
            
            # Gli indici delle etichette 1
            indices_labels_1 = np.where(concatenated_labels_by_label[label] == 1)[0]
            
            # Gli indici delle etichette 2
            indices_labels_2 = np.where(concatenated_labels_by_label[label] == 2)[0]
            
            # Indici iniziale e finale per le etichette 0 e 1
            start_idx_0 = indices_labels_0[0] if len(indices_labels_0) > 0 else None
            end_idx_0 = indices_labels_0[-1] if len(indices_labels_0) > 0 else None
            
            start_idx_1 = indices_labels_1[0] if len(indices_labels_1) > 0 else None
            end_idx_1 = indices_labels_1[-1] if len(indices_labels_1) > 0 else None
            
            start_idx_2 = indices_labels_2[0] if len(indices_labels_2) > 0 else None
            end_idx_2 = indices_labels_2[-1] if len(indices_labels_2) > 0 else None
    
    
            # **Print finale per verificare la concatenazione per ogni label**
            #print(f"\nCondizione: \033[1m{condition_triplet}\033[0m, Etichetta: {label}")
            #print(f"  - Shape dei dati concatenati per \033[1m{label}\033[0m: {concatenated_data_by_label[label].shape}")
            #print(f"  - Shape delle etichette concatenate per \033[1m{label}\033[0m: {concatenated_labels_by_label[label].shape}")
            
            # **Stampa la lista delle shapes delle etichette per ogni soggetto per questa etichetta**
            #print(f"\n  - Shape delle etichette per soggetto (per etichetta {label}): {shape_labels_per_subject[label]}\n")

            
            # **Stampa il conteggio totale delle etichette**
            #print(f"\n  - Totale delle etichette 0: {total_labels_0}")
            #print(f"  - Totale delle etichette 1: {total_labels_1}")
            #print(f"  - Totale delle etichette per la condizione: {total_labels}\n")

            # **Stampa gli indici per le etichette 0 e 1**
            # **OSSIA --> Stampa gli indici per l'etichetta corrente**
            
            #if label == 0:
            #    print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #else:
            #    print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}\n")

    
            #print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}")

    
        #ARRIVATI FINO A QUI, abbiamo che siccome stiamo iterando prima per tutti gli 0 e poi per tutti gli 1
        #Significa che, assumendo che siamo dentro 'baseline_vs_th_resp' e che 
        
        #'baseline' sia rappresentato dalle etichette 0
        #'th_resp' sia rappresentato dalle etichette 1
        
        #Al PRIMO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'baseline' per 'baseline_vs_th_resp'di tutti i soggetti)
        
        #Al SECONDO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #Quindi mi manca ancora 
        
        #A) CONCATENARE I DATI:
        
        #1)prima tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        
        #che verrà fatto dentro all_data (che è anch'esso una variabile dinamica!)
        
        #B) CONCATENARE LE LABELS:
        
        #1)prima tutti le labels (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti le labels (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #che verrà fatto dentro all_labels (che è anch'esso una variabile dinamica!)
        
        # Liste per raccogliere dati e labels di tutte le etichette
        
        # Qui dentro, invece, dov con
        all_data = []
        all_labels = []

        for label in concatenated_data_by_label.keys():
            all_data.append(concatenated_data_by_label[label])
            all_labels.append(concatenated_labels_by_label[label])
        
        
        #Alla fine, qui dentro avrò che, PER OGNI COPPIA DI CONDIZIONI SPERIMENTALI
        
        
        #'final_data' dovrebbe avere 
            #- prima tutti i dati di tutti i soggetti associati all'etichetta 0 
            #- e poi tutti i dati di tutti i soggetti associati all'etichetta 1
        
        #'final_labels' dovrebbe avere 
            #- prima tutte le labels di tutti i soggetti associati all'etichetta 0
            #- e poi tutte tutte le labels di tutti soggetti associati all'etichetta 1...

        
        # Concatenazione finale per la condizione corrente
        final_data = np.vstack(all_data)
        final_labels = np.hstack(all_labels)
    
        
        # Nome dinamico del dizionario
        #dict_name = f"{prefix}{condition_triplet}{suffix}"
        dict_name = f"{prefix}{condition_triplet}"

        # Salva il risultato nel dizionario globale
        all_subj_data_by_coupled_cond[dict_name] = {
            'data': final_data,
            'labels': final_labels
        }
        
    # Dopo aver costruito tutti i sotto-dizionari, iterare per stampare gli intervalli
    print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")

    for cond_key, cond_data in all_subj_data_by_coupled_cond.items():
        print(f"Condizione: \033[1m{cond_key}\033[0m\n")

        # Estrai le etichette dal sotto-dizionario
        labels = cond_data['labels']

        # Conta le etichette uniche
        unique_labels = np.unique(labels)

        # Variabile per il conteggio totale delle etichette
        total_labels = 0

        # Stampa gli intervalli di indici per ciascuna etichetta
        for label in unique_labels:

            # Trova gli indici corrispondenti a questa etichetta
            label_indices = np.where(labels == label)[0]

            # Determina l'intervallo
            start_idx = label_indices[0]
            end_idx = label_indices[-1]

            # Aggiungi il numero di occorrenze al conteggio totale
            total_labels += len(label_indices)

            # Stampa l'intervallo
            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m (Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

        # Stampa il totale delle etichette per la condizione corrente
        print(f"\nTotale etichette (0, 1 e 2): \033[1m{total_labels}\033[0m\n")

    return all_subj_data_by_coupled_cond

In [75]:
# Parametri

#baseline_vs_th_resp_vs_pt_resp
#baseline_vs_th_resp_vs_shared_resp
#baseline_vs_pt_resp_vs_shared_resp
#th_resp_vs_pt_resp_vs_shared_resp

conditions = ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp','baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']

prefix = "new_all_th_concat_spectrograms_"
#suffix = "_1_45"

tripled_conditions = list(new_subject_level_concatenations_triplets_exp_th_1_45['th_1'].keys())

# Chiamata alla funzione
new_concatenated_dictionaries_th = concatenate_all_single_subj_spectrograms_tripled_experimental_conditions_th(
    data_structure=new_subject_level_concatenations_spectrograms_triplets_exp_th,
    conditions=tripled_conditions,
    prefix=prefix,
    #suffix=suffix
)

# Stampa i risultati per verifica
print('\n\033[1mRISULTATO FINALE TUTTI I SOGGETTI TH\033[0m') 
for key, value in new_concatenated_dictionaries_th.items():
    print(f"{key}:")
    print(f"  Dati: {value['data'].shape}")
    print(f"  Labels: {value['labels'].shape}")


Soggetto: th_1, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 0, Shape: 51
Soggetto: th_1, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 1, Shape: 40
Soggetto: th_1, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 2, Shape: 40
Soggetto: th_2, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 0, Shape: 40
Soggetto: th_2, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 1, Shape: 43
Soggetto: th_2, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 2, Shape: 42
Soggetto: th_3, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 0, Shape: 40
Soggetto: th_3, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 1, Shape: 40
Soggetto: th_3, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 2, Shape: 40
Soggetto: th_4, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 0, Shape: 39
Soggetto: th_4, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 1, Shape: 53
Soggetto: th_4, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 2, Sh

##### STEP - Salvataggio Dataset di **All Single Therapists** EEG Data Spectrograms across **Triplets of Experimental Conditions** INSIEME

In [76]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [77]:
cd ..

/home/stefano/Interrogait


In [78]:
cd New_Plots_Sliding_Estimator_MNE_1_45

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [79]:
new_concatenated_dictionaries_th.keys()

dict_keys(['new_all_th_concat_spectrograms_baseline_vs_th_resp_vs_pt_resp', 'new_all_th_concat_spectrograms_baseline_vs_th_resp_vs_shared_resp', 'new_all_th_concat_spectrograms_baseline_vs_pt_resp_vs_shared_resp', 'new_all_th_concat_spectrograms_th_resp_vs_pt_resp_vs_shared_resp'])

In [80]:
#Mi estraggo ogni sotto-dizionario

new_all_th_concat_spectrograms_baseline_vs_th_resp_vs_pt_resp = new_concatenated_dictionaries_th['new_all_th_concat_spectrograms_baseline_vs_th_resp_vs_pt_resp']

new_all_th_concat_spectrograms_baseline_vs_th_resp_vs_shared_resp = new_concatenated_dictionaries_th['new_all_th_concat_spectrograms_baseline_vs_th_resp_vs_shared_resp']

new_all_th_concat_spectrograms_baseline_vs_pt_resp_vs_shared_resp = new_concatenated_dictionaries_th['new_all_th_concat_spectrograms_baseline_vs_pt_resp_vs_shared_resp']

new_all_th_concat_spectrograms_th_resp_vs_pt_resp_vs_shared_resp = new_concatenated_dictionaries_th['new_all_th_concat_spectrograms_th_resp_vs_pt_resp_vs_shared_resp']


In [81]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_NF '''
import pickle
   
#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

#'BASELINE VS TH RESP VS PT RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_all_th_concat_spectrograms_baseline_vs_th_resp_vs_pt_resp.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_spectrograms_baseline_vs_th_resp_vs_pt_resp, f)
                                  
#'BASELINE VS TH RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_all_th_concat_spectrograms_baseline_vs_th_resp_vs_shared_resp.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_spectrograms_baseline_vs_th_resp_vs_shared_resp, f)
        
#'BASELINE VS PT RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_all_th_concat_spectrograms_baseline_vs_pt_resp_vs_shared_resp.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_spectrograms_baseline_vs_pt_resp_vs_shared_resp, f)
    
#'TH RESP VS PT RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_all_th_concat_spectrograms_th_resp_vs_pt_resp_vs_shared_resp.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_spectrograms_th_resp_vs_pt_resp_vs_shared_resp, f)


### STEP 4.3.2.3.2 - All Patients EEG Data Reconstructions (2-DWT)

#### Concatenazione All Single Subject Data (PT) per tutte le condizioni sperimentali, per ogni livello di ricostruzione (θ+δ, θ and δ)

In [82]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [83]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''

#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('all_subjects_condition_results_th.pkl', 'rb') as f:
#    all_subjects_condition_results_th = pickle.load(f)
    
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_all_subjects_condition_results_pt_2D.pkl', 'rb') as f:
    new_all_subjects_condition_results_pt_2D = pickle.load(f)

FileNotFoundError: [Errno 2] No such file or directory: 'new_all_subjects_condition_results_pt_2D.pkl'

In [ ]:
new_all_subjects_condition_results_pt_2D.keys()

In [ ]:
#print(f"\033[1mChiavi di primo ordine\033[0m i.e., all_subjects_condition_results_th: \n\n{all_subjects_condition_results_th.keys()}")
#print(f"\n\n\033[1mChiavi di ogni condizione sperimentale\033[0m, i.e., 'wave_baseline_1': {all_subjects_condition_results_th['wave_baseline_1'].keys()}")

#all_subjects_condition_results['wave_baseline_1'].keys()


print(f"\033[1mChiavi di primo ordine\033[0m i.e., new_all_subjects_condition_results_pt_2D: \n\n{new_all_subjects_condition_results_pt_2D.keys()}")
print(f"\n\n\033[1mChiavi di ogni condizione sperimentale\033[0m, i.e., 'wave_baseline_1': {new_all_subjects_condition_results_pt_2D['wave_baseline_1'].keys()}")


In [ ]:
#new_all_subjects_condition_results_th['wave_baseline_1'].keys()
print(new_all_subjects_condition_results_pt_2D['wave_baseline_1']['A'].shape)
print(new_all_subjects_condition_results_pt_2D['wave_baseline_1']['D'].shape)

In [ ]:
'''
Da "all_subjects_condition_results" ottengo:

Le ricostruzioni 4° e 5° livello di tutti i terapisti per tutte le condizioni sperimentali dai coefficienti di approssimazione
Le ricostruzioni 5° livello di tutti i terapisti per tutte le condizioni sperimentali dai coefficienti di dettaglio

				(i.e., single_th_all_extracted_reconstructions):

'''

import numpy as np

# Definizione degli indici dei canali desiderati
selected_channels = [12, 30, 48]  # Indici per Fz, Cz, Pz

# Creazione di un dizionario dei dati di tutti i terapisti singolarmente, per salvare le ricostruzioni estratte per livello 4 e 5
#single_th_all_extracted_reconstructions = {}

new_single_pt_all_extracted_reconstructions_2D = {}

# Iterazione su tutte le condizioni sperimentali di tutti i soggetti 

#'OLD VERSION'
#for condition, data in all_subjects_condition_results_th.items():

for condition, data in new_all_subjects_condition_results_pt_2D.items():
    
    # Estrarre le etichette per questa condizione
    A_labels = data['A_labels']
    
    # Estrazione della matrice 'A' per le ricostruzioni del segnale con coefficienti di approssimazione
    A = data['A']
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Estrazione della matrice 'D' per le ricostruzioni del segnale con coefficienti di approssimazione
    D = data['D']
    
    # Estrarre solo i canali selezionati e i livelli di ricostruzione desiderati (4° e 5°, quindi indice -2 e -1)
    theta_reconstruction = A[:, selected_channels, :, -2]  # 4° livello di ricostruzione
    delta_reconstruction = A[:, selected_channels, :, -1]  # 5° livello di ricostruzione
    
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Ottenere i coefficienti di dettaglio del 5° livello di ricostruzione (theta range)
    coeff_fifth_detail_theta = D[:, selected_channels, :, -1]  # Coefficienti di dettaglio del livello 5
    
    
    # Trasponi per ottenere la forma desiderata: (trials, canali, punti temporali)
    theta_reconstruction = theta_reconstruction.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    delta_reconstruction = delta_reconstruction.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    coeff_fifth_detail_theta = coeff_fifth_detail_theta.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Creare un sotto-dizionario per organizzare 
    #le ricostruzioni EEG del livello 4 'theta' e livello 5 'delta' dai coeff di approx
    #le ricostruzioni EEG del livello 4 'theta' e livello 5 'delta' dai coeff di detail
    
    new_single_pt_all_extracted_reconstructions_2D[condition] = {
        'theta': theta_reconstruction,
        'delta': delta_reconstruction,
        'coeff_fifth_detail_theta': coeff_fifth_detail_theta, 
        'labels': A_labels
    }

# Verifica delle dimensioni del risultato estratto per una condizione specifica
print(f"\t\t\033[1mRicostruzioni 4° e 5° livello di tutti i terapisti per tutte le condizioni sperimentali")
#print(f"\n\n\t\t\t\t(i.e., \033[1msingle_th_all_extracted_reconstructions\033[0m):\n")

print(f"\n\n\t\t\t\t(i.e., \033[1mnew_single_pt_all_extracted_reconstructions_2D\033[0m):\n")


#for condition, extracted_data in single_pt_all_extracted_reconstructions.items():

#'''AGGIUNTI COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''

for condition, extracted_data in new_single_pt_all_extracted_reconstructions_2D.items():
    
    print(f"Condizione: \033[1m{condition}\033[0m, "
          f"Theta shape: \033[1m{extracted_data['theta'].shape}\033[0m, "
          f"Delta shape: \033[1m{extracted_data['delta'].shape}\033[0m, "
          f"Coeff Fifth Detail shape: \033[1m{extracted_data['coeff_fifth_detail_theta'].shape}\033[0m, "
          f"Labels: \033[1m{len(extracted_data['labels'])}\033[0m")

# STEP 2: Concatenare i dati e le etichette di tutti i soggetti per i livelli di ricostruzione 4 e 5

# Inizializzazione delle liste per raccogliere i dati e le etichette del 4° e 5° livello di ricostruzione da coeff approx

all_pt_fourth = []
labels_pt_fourth = []
exp_conditions_fourth = []

all_pt_fifth = []
labels_pt_fifth = []
exp_conditions_fifth = []


#'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''

all_pt_fifth_detail = []
labels_pt_fifth_detail = []
exp_conditions_fifth_detail = []

# Iterazione su tutte le condizioni sperimentali

#for condition, data in single_th_all_extracted_reconstructions.items():
for condition, data in new_single_pt_all_extracted_reconstructions_2D.items():    
    
    # Preparazione delle liste per dati e etichette per ogni condizione
    dati_fourth = [None] * 4  # Per 'baseline', 'th_resp', 'vision_resp', 'shared_resp'
    labels_fourth = [None] * 4
    
    dati_fifth = [None] * 4
    labels_fifth = [None] * 4
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    dati_fifth_detail = [None] * 4
    labels_fifth_detail = [None] * 4
    
    for chiave, valore in data.items():
        
        if chiave == 'theta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            if 'baseline' in condition:
                dati_fourth[0] = valore
                labels_fourth[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fourth[1] = valore
                labels_fourth[1] = data['labels']
            
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fourth[2] = valore
                labels_fourth[2] = data['labels']
                
            elif 'shared_resp' in condition:
                dati_fourth[3] = valore
                labels_fourth[3] = data['labels']
                
        elif chiave == 'delta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            if 'baseline' in condition:
                dati_fifth[0] = valore
                labels_fifth[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fifth[1] = valore
                labels_fifth[1] = data['labels']
            
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fifth[2] = valore
                labels_fifth[2] = data['labels']
                
                
            elif 'shared_resp' in condition:
                dati_fifth[3] = valore
                labels_fifth[3] = data['labels']
        
        elif chiave == 'coeff_fifth_detail_theta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            
            if 'baseline' in condition:
                dati_fifth_detail[0] = valore
                labels_fifth_detail[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fifth_detail[1] = valore
                labels_fifth_detail[1] = data['labels']
                
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fifth_detail[2] = valore
                labels_fifth_detail[2] = data['labels']
                
            elif 'shared_resp' in condition:
                dati_fifth_detail[3] = valore
                labels_fifth_detail[3] = data['labels']
                
            
    # Filtrare i valori non None
    dati_fourth = [d for d in dati_fourth if d is not None]
    labels_fourth = [l for l in labels_fourth if l is not None]
    
    dati_fifth = [d for d in dati_fifth if d is not None]
    labels_fifth = [l for l in labels_fifth if l is not None]
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    dati_fifth_detail = [d for d in dati_fifth_detail if d is not None]
    labels_fifth_detail = [l for l in labels_fifth_detail if l is not None]
    
    # Concatenare i dati e le etichette
    if dati_fourth:
        datas_fourth = np.concatenate(dati_fourth, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fourth = np.concatenate([np.array(l) for l in labels_fourth], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_pt_fourth.append(datas_fourth)
        labels_pt_fourth.append(labels_fourth)
        exp_conditions_fourth.append(condition)
    
    if dati_fifth:
        datas_fifth = np.concatenate(dati_fifth, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fifth = np.concatenate([np.array(l) for l in labels_fifth], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_pt_fifth.append(datas_fifth)
        labels_pt_fifth.append(labels_fifth)
        exp_conditions_fifth.append(condition)
    
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    if dati_fifth_detail:
        
        datas_fifth_detail = np.concatenate(dati_fifth_detail, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fifth_detail = np.concatenate([np.array(l) for l in labels_fifth_detail], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_pt_fifth_detail.append(datas_fifth_detail)
        labels_pt_fifth_detail.append(labels_fifth_detail)
        exp_conditions_fifth_detail.append(condition)

# STEP 3: Concatenazione finale di tutti i dati e le etichette

# Concatenazione finale di tutti i dati e le etichette

#'''PER COEFFICIENTI DI APPROSSIMAZIONE 4° LIVELLO (i.e., range 0-7.812Hz)'''
if all_pt_fourth:
    all_fourth = np.concatenate(all_pt_fourth, axis=0)
else:
    all_fourth = np.array([])

if labels_pt_fourth:
    all_fourth_labels = np.concatenate(labels_pt_fourth, axis=0)
else:
    all_fourth_labels = np.array([])

    
#'''PER COEFFICIENTI DI APPROSSIMAZIONE 5° LIVELLO (i.e., range 0-3.9Hz)'''    
if all_pt_fifth:
    all_fifth = np.concatenate(all_pt_fifth, axis=0)
else:
    all_fifth = np.array([])

if labels_pt_fifth:
    all_fifth_labels = np.concatenate(labels_pt_fifth, axis=0)
else:
    all_fifth_labels = np.array([])
    

#'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
if all_pt_fifth_detail:
    all_fifth_detail = np.concatenate(all_pt_fifth_detail, axis=0)
else:
    all_fifth_detail = np.array([])

if labels_pt_fifth_detail:
    all_fifth_detail_labels = np.concatenate(labels_pt_fifth_detail, axis=0)
else:
    all_fifth_detail_labels = np.array([])
    

# Verifica delle dimensioni del risultato finale
print(f"\n\n\n\t\tTUTTI I TRIAL DI TUTTI I SOGGETTI DI OGNI CONDIZIONE SPERIMENTALE - PER LIVELLO DI RICOSTRUZIONE ")

print(f"\n\033[1m4° livello\033[0m di ricostruzione da Coeff di Approx - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fourth\033[0m: \033[1m{all_fourth.shape}\033[0m, Length di \033[1mall_fourth_labels\033[0m: \033[1m{len(all_fourth_labels)}\033[0m")

print(f"\n\033[1m5° livello\033[0m di ricostruzione da Coeff di Approx - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fifth\033[0m: \033[1m{all_fifth.shape}\033[0m, Length di \033[1mall_fifth_labels\033[0m: \033[1m{len(all_fifth_labels)}\033[0m")

print(f"\n\033[1m5° livello\033[0m di ricostruzione da Coeff di Detail - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fifth_detail\033[0m: \033[1m{all_fifth_detail.shape}\033[0m, Length di \033[1mall_fifth_detail_labels\033[0m: \033[1m{len(all_fifth_detail_labels)}\033[0m")


In [ ]:
!pwd

In [ ]:
#Salvo ricostruzioni 4° e 5° livello per singolo terapista con concatenazioni dati e labels 

''' PATH  --> cd Plots_Sliding_Estimator_MNE '''

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('single_th_all_extracted_reconstructions.pkl', 'wb') as f:
#    pickle.dump(single_th_all_extracted_reconstructions, f)
    
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''

import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_single_pt_all_extracted_reconstructions_2D.pkl', 'wb') as f:
    pickle.dump(new_single_pt_all_extracted_reconstructions_2D, f)


In [ ]:
'''SALVO IN UN GRANDE DIZIONARIO I DATI E LE LABELS CONCATENATI DI TUTTI I SOGGETTI PER IL LIVELLO DI RICOSTRUZIONE'''


#Creo dizionario per le concatenazioni di dati e labels a seconda del livello di ricostruzione del segnale EEG 
new_all_pt_concat_reconstructions_2D = {'all_pt_fourth': all_fourth, 
                                 'all_pt_fourth_labels': all_fourth_labels,
                                 'all_pt_fifth': all_fifth,
                                 'all_pt_fifth_labels': all_fifth_labels,
                                 'all_pt_fifth_detail': all_fifth_detail,
                                 'all_pt_fifth_detail_labels': all_fifth_detail_labels
                                }

'''STAMPA DELLE CHIAVI e SHAPE'''
#all_th_concat_reconstructions.keys()
#all_th_concat_reconstructions['all_th_fourth'].shape
#all_th_concat_reconstructions['all_th_fourth_labels'].shape

#all_th_concat_reconstructions['all_th_fifth'].shape
#all_th_concat_reconstructions['all_th_fifth_labels'].shape



#all_th_concat_theta = {'all_th_fourth': all_fourth, 
#                       'all_th_fourth_labels': all_fourth_labels}


#all_th_concat_delta = {'all_th_fifth': all_fifth,
#                       'all_th_fifth_labels': all_fifth_labels}


#all_th_concat_theta.keys()
#all_th_concat_delta.keys()

In [ ]:
new_all_pt_concat_reconstructions_2D.keys()

In [ ]:
!pwd

In [ ]:
'''SALVO I DATI CONCATENATI DI TUTTI I SOGGETTI TERAPISTI, RISPETTO AD UNO SPECIFICO LIVELLO DI RICOSTRUZIONE

import pickle
# Salvare l'intero dizionario annidato con pickle
with open('all_fourth_th_2D.pkl', 'wb') as f:
    pickle.dump(all_fourth, f) 


import pickle
# Salvare l'intero dizionario annidato con pickle
with open('all_fifth_th_2D.pkl', 'wb') as f:
    pickle.dump(all_fifth, f) 

    
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_fifth_detail_th_2D.pkl', 'wb') as f:
    pickle.dump(all_fifth_detail, f) 
'''

#SALVO I DATI CONCATENATI DI TUTTI I SOGGETTI TERAPISTI, RISPETTO AD OGNI LIVELLO DI RICOSTRUZIONE INSIEME
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_pt_concat_reconstructions_2D.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_2D, f)   
    


In [ ]:
#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_single_th_all_extracted_reconstructions.pkl', 'rb') as f:
#    new_single_th_all_extracted_reconstructions = pickle.load(f)

In [ ]:
#Dizionario con dati e labels 
#a seconda del livello di ricostruzione del segnale EEG 
#di ogni singolo soggetto 
#per tutte le condizioni sperimentali SEPARATAMENTE!

'''OLD'''
#print(f"\n\033[1msingle_th_all_extracted_reconstructions.keys()\033[0m: \n{single_th_all_extracted_reconstructions.keys()}\n")
#print(f"\n\033[1msingle_th_all_extracted_reconstructions['wave_baseline_1'].keys()\033[0m: {single_th_all_extracted_reconstructions['wave_baseline_1'].keys()}")


'''NEW'''
print(f"\n\033[1mnew_single_pt_all_extracted_reconstructions_2D.keys()\033[0m: \n{new_single_pt_all_extracted_reconstructions_2D.keys()}\n")
print(f"\n\033[1mnew_single_pt_all_extracted_reconstructions_2D['wave_baseline_1'].keys()\033[0m: {new_single_pt_all_extracted_reconstructions_2D['wave_baseline_1'].keys()}")


#single_th_all_extracted_reconstructions['wave_baseline_1']['theta'].shape
#single_th_all_extracted_reconstructions['wave_baseline_1']['delta'].shape
#len(single_th_all_extracted_reconstructions['wave_baseline_1']['labels'])

In [ ]:
# Itera su ogni chiave nel dizionario new_single_th_all_extracted_reconstructions
for main_key in new_single_pt_all_extracted_reconstructions_2D.keys():
    
    # Verifica se 'coeff_fifth_detail_theta' è presente tra le sottochiavi
    if 'coeff_fifth_detail_theta' not in new_single_pt_all_extracted_reconstructions_2D[main_key]:
        print(f"La chiave '{main_key}' \033[1mNON contiene\033[0m 'coeff_fifth_detail_theta'")
    else:
        print(f"La chiave '{main_key}' contiene 'coeff_fifth_detail_theta'")

In [ ]:
'''
Questa struttura consente di avere i dati correttamente organizzati e concatenati per ogni soggetto 
in base al livello di ricostruzione, 
mantenendo la corrispondenza tra dati e etichette per ogni condizione sperimentale

Da           "single_th_all_extracted_reconstructions_2D"       a            "subject_level_concatenations_th_2D"

Da           "new_single_th_all_extracted_reconstructions_2D"       a       "new_subject_level_concatenations_th_2D"
'''

import numpy as np

# Dizionario per contenere i dati concatenati per ogni soggetto e livello di ricostruzione
new_subject_level_concatenations_pt_2D = {}

# Variabile per tracciare il soggetto precedente
previous_subject_suffix = None

print(f"\t\t\033[1mConcatenazione dati 4° e 5° livello di OGNI terapista di TUTTE le condizioni sperimentali INSIEME\033[0m")
#print(f"\n\t\tda\t\033[1m'single_th_all_extracted_reconstructions'\033[0m \ta\t\033[1m'subject_level_concatenations_th'\033[0m")

print(f"\n\tda\033[1m'new_single_pt_all_extracted_reconstructions_2D'\033[0m \ta\t\033[1m'new_subject_level_concatenations_pt_2D'\033[0m")

# Iterazione su tutte le chiavi di single_th_all_extracted_reconstructions

#'''OLD VERSION'''
#for condition, data in single_th_all_extracted_reconstructions.items():

for condition, data in new_single_pt_all_extracted_reconstructions_2D.items():
    
    # Estrazione del suffisso numerico del soggetto (es. '1', '2', ...)
    subject_suffix = condition.split('_')[-1]  # Prende solo la parte numerica
    
    # Creazione del nome della chiave del soggetto specifico
    subj_name = f'pt_{subject_suffix}'  # Crea la chiave con prefisso 'th_' e suffisso numerico
    
    # Se stiamo per passare a un nuovo soggetto, stampiamo le dimensioni delle concatenazioni per il soggetto precedente
    if previous_subject_suffix is not None and subject_suffix != previous_subject_suffix:
        
        print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('th_{previous_subject_suffix}'):\033[0m\n")
        prev_subject_name = f'pt_{previous_subject_suffix}'
        
        #levels = subject_level_concatenations_th[prev_subject_name]
        
        levels = new_subject_level_concatenations_pt_2D[prev_subject_name]
        
        # Concatenazione dei dati prima della stampa
        theta_concat = np.concatenate(levels['theta'], axis=0)
        delta_concat = np.concatenate(levels['delta'], axis=0)
        
        #Coefficienti di dettaglio 5° livello theta
        theta_concat_strict = np.concatenate(levels['theta_strict'], axis=0)
        
        labels_concat = np.concatenate(levels['labels'], axis=0)
        
        #if 'coeff_fifth_detail_theta' not in levels:
        #    print(f"La chiave 'coeff_fifth_detail_theta' non è presente per il soggetto: {prev_subject_name}")

        print(f"Soggetto: \033[1m{prev_subject_name}\033[0m, "
              f"Theta shape: \033[1m{np.concatenate(levels['theta'], axis=0).shape}\033[0m, "
              f"Delta shape: \033[1m{np.concatenate(levels['delta'], axis=0).shape}\033[0m, "
              f"Theta Strict shape: \033[1m{np.concatenate(levels['theta_strict'], axis=0).shape}\033[0m, "
              f"Labels length: \033[1m{len(np.concatenate(levels['labels'], axis=0))}\033[0m")
        
        
        #'''OLD'''
        # Salvataggio dei dati concatenati nel dizionario come array NumPy
        #subject_level_concatenations_th[prev_subject_name]['theta'] = theta_concat
        #subject_level_concatenations_th[prev_subject_name]['delta'] = delta_concat
        #subject_level_concatenations_th[prev_subject_name]['labels'] = labels_concat
        
        
        #'''NEW'''
        new_subject_level_concatenations_pt_2D[prev_subject_name]['theta'] = theta_concat
        new_subject_level_concatenations_pt_2D[prev_subject_name]['delta'] = delta_concat
        
        new_subject_level_concatenations_pt_2D[prev_subject_name]['theta_strict'] = theta_concat_strict
        
        new_subject_level_concatenations_pt_2D[prev_subject_name]['labels'] = labels_concat
    
    #'''OLD'''
    # Inizializzare il dizionario per il soggetto specifico se non esiste già
    #if subj_name not in subject_level_concatenations_th:
    #    subject_level_concatenations_th[subj_name] = {
    #        'theta': [],
    #        'delta': [],
    #        'labels': []
    #    }
    
    #'''NEW'''
    if subj_name not in new_subject_level_concatenations_pt_2D:
        new_subject_level_concatenations_pt_2D[subj_name] = {
            'theta': [],
            'delta': [],
            'theta_strict': [],
            'labels': []
        }
        
    # Stampiamo le informazioni per ogni condizione
    print(f"\n\n\nSoggetto: \033[1m{subj_name}\033[0m, Condizione: \033[1m{condition}\033[0m")
    print(f"  - Theta shape: \033[1m{data['theta'].shape}\033[0m")
    print(f"  - Delta shape: \033[1m{data['delta'].shape}\033[0m")
    print(f"  - Theta Strict: \033[1m{data['coeff_fifth_detail_theta'].shape}\033[0m")
    print(f"  - Labels shape: \033[1m{len(data['labels'])}\033[0m")
    print(f"  - Valori unici delle etichette: \033[1m{np.unique(data['labels'])}\033[0m")
    
    
    #'''OLD'''
    # Concatenazione dei dati per i livelli theta, delta e labels
    #subject_level_concatenations_th[subj_name]['theta'].append(data['theta'])
    #subject_level_concatenations_th[subj_name]['delta'].append(data['delta'])
    #subject_level_concatenations_th[subj_name]['labels'].append(data['labels'])
    
    
    #'''NEW'''
    
    # Concatenazione dei dati per i livelli theta, delta e labels
    new_subject_level_concatenations_pt_2D[subj_name]['theta'].append(data['theta'])
    new_subject_level_concatenations_pt_2D[subj_name]['delta'].append(data['delta'])
    
    new_subject_level_concatenations_pt_2D[subj_name]['theta_strict'].append(data['coeff_fifth_detail_theta'])
    
    new_subject_level_concatenations_pt_2D[subj_name]['labels'].append(data['labels'])
    
    # Aggiorna il soggetto precedente
    previous_subject_suffix = subject_suffix

# Dopo aver iterato su tutte le condizioni, concatenare e stampare le informazioni dell'ultimo soggetto
if previous_subject_suffix is not None:
    
    last_subject_name = f'pt_{previous_subject_suffix}'
    #levels = subject_level_concatenations_th[last_subject_name]
    levels = new_subject_level_concatenations_pt_2D[last_subject_name]
    
    print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('{last_subject_name}'):\033[0m\n")
    
    # Concatenazione dei dati dell'ultimo soggetto
    theta_concat = np.concatenate(levels['theta'], axis=0)
    delta_concat = np.concatenate(levels['delta'], axis=0)
    
    theta_concat_strict = np.concatenate(levels['theta_strict'], axis=0)
    
    labels_concat = np.concatenate(levels['labels'], axis=0)
    
    #'''OLD'''
    # Salvataggio dei dati concatenati dell'ultimo soggetto nel dizionario come array NumPy
    #subject_level_concatenations_th[last_subject_name] = {
    #    'theta': theta_concat,
    #    'delta': delta_concat,
    #    'labels': labels_concat
    #}
    
    #'''NEW'''
    # Salvataggio dei dati concatenati dell'ultimo soggetto nel dizionario come array NumPy
    new_subject_level_concatenations_pt_2D[last_subject_name] = {
       'theta': theta_concat,
        'delta': delta_concat,
        'theta_strict': theta_concat_strict,
        'labels': labels_concat
    }
    
    
    print(f"Soggetto: \033[1m{last_subject_name}\033[0m, "
          f"Theta shape: \033[1m{np.concatenate(levels['theta'], axis=0).shape}\033[0m, "
          f"Delta shape: \033{np.concatenate(levels['delta'], axis=0).shape}\033[0m, "
          f"Labels length: \033[1m{len(np.concatenate(levels['labels'], axis=0))}\033[0m\n\n")



In [ ]:
'''CHIAVI DI TUTTO IL DIZIONARIO '''
#subject_level_concatenations_th.keys()


new_subject_level_concatenations_pt_2D.keys()


#SOGGETTO 1

#CHIAVI
#subject_level_concatenations_th['th_1'].keys()

#DATI
#subject_level_concatenations_th['th_1']['theta'].shape

#new_subject_level_concatenations_th['th_1']['theta'].shape

#subject_level_concatenations_th['th_1']['delta'].shape

#LABELS
#subject_level_concatenations_th['th_1']['labels'].shape)
#type(subject_level_concatenations_th['th_1']['labels'])

# Check della concantenazione delle labels TH_1

#subject_level_concatenations_th['th_1']['labels'][:42]
#subject_level_concatenations_th['th_1']['labels'][41:81]
#subject_level_concatenations_th['th_1']['labels'][81:120]
#subject_level_concatenations_th['th_1']['labels'][121:164]

In [ ]:
#subject_level_concatenations_th['th_15']['labels'].shape

In [ ]:
#subject_level_concatenations_th['th_1'].keys()

new_subject_level_concatenations_pt_2D['pt_19'].keys()


In [ ]:
#unique_values, counts = np.unique(subject_level_concatenations_th['th_1']['labels'], return_counts=True)

#unique_values, counts = np.unique(new_subject_level_concatenations_th['th_1']['labels'], return_counts=True)

In [ ]:
#unique_values
#counts
#counts[0]

In [ ]:
!pwd

In [ ]:
#Salvo ricostruzioni 4° e 5° livello per singolo terapista con concatenazioni dati e labels 

    
''' PATH  --> cd Plots_Sliding_Estimator_MNE '''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('subject_level_concatenations_pt.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations_pt, f)
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt_2D.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_pt_2D, f)


### STEP 4.3.2.3.2.1 - All Patients EEG Data Reconstructions (**STFT**)

#### **Calcolo Spettrogrammi** All **SINGLE** Subject Data (**PT**) per **Tutte le Condizioni sperimentali**

In [84]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [85]:
cd ..

/home/stefano/Interrogait


In [86]:
cd New_Plots_Sliding_Estimator_MNE_1_45

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [87]:
# Caricare l'intero dizionario annidato con pickle
import pickle

fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{fam_path}patients_data.pkl', 'rb') as f:
    patients_data = pickle.load(f)

In [88]:
print(len(patients_data))
print(patients_data[0].keys())

20
dict_keys(['baseline_1', 'th_resp_1', 'pt_resp_1', 'shared_resp_1', 'baseline_1_labels', 'th_resp_1_labels', 'pt_resp_1_labels', 'shared_resp_1_labels'])


In [ ]:
'''CREAZIONE SPETTROGRAMMI FREQUENZE x TEMPO'''

import numpy as np
import pywt
from scipy.signal import stft

def create_spectograms_from_stft(data, window_size = 50, step_size = 25, fs = 250):
    
    # Dizionario per memorizzare i risultati separati per condizione sperimentale
    condition_results = {}
    
    for idx, data_dict in enumerate(data):
        print(f"\n\n\t\t\t\t\t\033[1mProcessing Subject {idx + 1}\033[0m:\n")

        for condition, value in data_dict.items():
            if '_labels' in condition:
                base_condition = condition.replace('_labels', '')  # Rimuove '_labels'
                condition_key = base_condition
                labels_key = condition
            else:
                base_condition = condition
                condition_key = base_condition
                labels_key = f'{base_condition}_labels'
            
            # Aggiungi chiavi inizializzate per nuove condizioni
            if '_labels' not in condition and condition_key not in condition_results:
                condition_results[condition_key] = {'spectrograms': [], 'labels': []}
            
            # Applicazione wavelet solo per array np.ndarray
            if isinstance(value, np.ndarray):
                print(f"\nApplicazione STFT per '\033[1m{condition_key}\033[0m'\n")
                print(f"\033[1mShape\033[0m dei dati per \033[1m{condition_key}\033[0m: {value.shape}")
                
                
                # Esegui STFT per ogni canale e trial          
                
                #La funzione stft di SciPy restituisce uno spettrogramma con la forma (n_frequencies, n_time_steps),
                #quindi:38 corrisponde al numero di bin di frequenza calcolati a partire dalla finestra FFT di 75 punti.
                
                #Infatti, per una finestra di lunghezza 75, il numero di bin è calcolato (in questo caso, dato che 75 è dispari) come (75 + 1) // 2, ovvero 38.
                #Il numero di passi temporali (n_time_steps) viene invece calcolato in base alla lunghezza del segnale e ai parametri di finestra e overlap.
                
                #Nel tuo caso, estraendo 250 punti (da 50 a 300) con nperseg=75 e noverlap=25 (cioè con un salto di 50 campioni per finestra), 
                #il numero di segmenti dovrebbe essere:
                #1 + [250−75/75-25] = 1 + [175/50]  = 1 + 3 = 4

                #Pertanto, il risultato di stft (cioè Zxx) ha forma (38, 4) e non (4, 38). 
                #Se ti aspetti una struttura con l'asse del tempo come terza dimensione (ad esempio, (trial, canali, tempo, frequenze))
                #potresti dover trasporre l'array in modo da scambiare le dimensioni frequenza e tempo.
                
                '''
                1) crearmi una lista per salvarmi poi tutti gli spettrogrammi di tutti i trials
                2) per il trials corrente mi salvo lo spettrogramma e lo appendo poi ad 1)
                3) converto la lista di tutti gli spettrogrammi di tutti i trials della condizione corrente in array numpy 
                4) carico poi l'array numpy dentro il dizionario della condizione corrente dentro la chiave 'spectrograms'
                '''
                
                all_trial_spectrograms = []

                for trial in range(value.shape[0]):
                    single_trial_spectrograms = []  # Lista per memorizzare gli spettrogrammi per il trial corrente

                    for channel in range(value.shape[1]):
                        
                        single_channel_data = value[trial, channel, 50:300]  # Estrai i dati del singolo canale
                        
                        #print(f"Segment length: {len(single_channel_data)}")
                    
                        '''TIENI A MENTE CHE DUE PARAMETRI GESTISCONO IL PADDING QUI AUTOMATICAMENTE, CHE SONO:
                        
                        boundary='zeros', 
                        padded=True,
                        
                        PER QUESTO MOTIVO LE FINESTRE SARANNO 11 E NON 9.
                        
                        IN QUESTO MODO, SI MIGLIORA LA RISOLUZIONE IN FREQUENZA ALL'INIZIO E FINE DEL SEGNALE (DI 250 PUNTI!)
                        ANDANDO IN QUESTO MODO A RIDURRE GLI EFFETTI DI BORDO
                        '''
                        
                        f, t, Zxx = stft(single_channel_data, fs=fs, window='hann', nperseg=window_size, noverlap=step_size)
                        
                        single_trial_spectrograms.append(Zxx)  # Aggiungi lo spettrogramma calcolato per il canale corrente

                    all_trial_spectrograms.append(np.array(single_trial_spectrograms))  # Forma: (numero_canali, frequenze, tempo)

                condition_results[condition_key]['spectrograms'].extend(all_trial_spectrograms)

                # Gestione etichette
                if labels_key in data_dict:
                    num_labels = data_dict[labels_key]
                    if condition_key in condition_results:
                        print(f"\nFound labels for condition \033[1m{labels_key}\033[0m, length: \033[1m{len(num_labels)}\033[0m\n")
                        condition_results[condition_key]['labels'].extend(num_labels)
            else:
                print(f"\033[1m{labels_key}\033[0m' non è un np.array, non applicare la STFT ")
    
    # Preparazione risultati concatenati
    all_subjects_condition_results = {}

    for condition_key, results in condition_results.items():
        if "_labels" in condition_key or len(results['spectrograms']) == 0:  # Verifica che ci siano spettrogrammi
            print(f"\nSkipping \033[1m{labels_key}\033[0m as it is a label or has no valid data.")
            continue

        wave_condition_name = f'spectrograms_{condition_key}'
        print(f"\n\nResults for \t\t\t\t\t\033[1m{wave_condition_name}\033[0m:\n\n")

        # Converti in un array NumPy 3D finale
        spectrograms_4d = np.array(results['spectrograms'])  # Forma: (numero_di_trial, numero_canali, frequenze, tempo)
        all_subjects_condition_results[wave_condition_name] = {
            'spectrograms_4d': spectrograms_4d,
            'labels': results['labels']
        }

        print(f"spectrograms_4d shape: {spectrograms_4d.shape}")
    
    '''
    Quindi alla fine si avrà una shape del tipo (44, 61, 38, 7) dove indica che avrai
    uno spettrogramma per ciascun trial, per ciascun canale, 
    che contiene informazioni sulle bande di frequenza e sui punti temporali. 
    
    Questa struttura è perfetta per essere utilizzata come input per una rete neurale convoluzionale (CNN),
    poiché la rete può apprendere dalle relazioni spaziali e temporali nei dati.
    '''
    
    return all_subjects_condition_results


In [ ]:
'''CREAZIONE SPETTROGRAMMI ELETTRODI x FREQUENZE - VERSIONE NON CORRETTA


Spiegazione delle modifiche

1) Aggregazione lungo l'asse temporale:
    Per ogni canale, dopo aver calcolato la STFT (che restituisce un array di shape (n_frequencies, n_time_steps)), 
    si calcola la media lungo il tempo (axis=1). 

In questo modo ottieni un vettore che rappresenta la distribuzione di potenza per ciascuna frequenza.

2) Riorganizzazione dei dati:
    Accumulando questi vettori per tutti gli elettrodi, ottieni un array di shape (n_channels, n_frequencies).
    
    Trasponendo questo array, ottieni una "mappa" 2D dove:

    Le righe corrispondono alle frequenze (asse y).
    Le colonne corrispondono agli elettrodi (asse x).
    
Risultato finale:
Il dizionario finale conterrà, per ciascuna condizione, un array 3D in cui ogni trial è rappresentato da un'immagine 2D con dimensioni 
(n_frequencies, n_channels). 

Questa struttura dovrebbe essere più adatta sia per una rete neurale CNN che per interpretazioni con Grad-CAM, 
in quanto mostra esplicitamente come ogni elettrodo contribuisce a ciascuna banda di frequenza.

Questa modifica risponde alla richiesta del supervisore: riorganizzare i dati in modo che la rappresentazione 2D evidenzi 
la distribuzione delle frequenze per ogni elettrodo, facilitando l'interpretazione del Gradcam.

'''

import numpy as np
from scipy.signal import stft

def create_spectograms_from_stft_electrode_freq(data, window_size=50, step_size=25, fs=250):
    
    # Dizionario per memorizzare i risultati per ciascuna condizione sperimentale
    condition_results = {}
    
    for idx, data_dict in enumerate(data):
        print(f"\n\n\t\t\t\t\t\033[1mProcessing Subject {idx + 1}\033[0m:\n")
        
        for condition, value in data_dict.items():
            # Gestione delle chiavi per condizioni e relative label
            if '_labels' in condition:
                base_condition = condition.replace('_labels', '')
                condition_key = base_condition
                labels_key = condition
            else:
                base_condition = condition
                condition_key = base_condition
                labels_key = f'{base_condition}_labels'
            
            # Inizializza la struttura per la condizione se non esiste
            if '_labels' not in condition and condition_key not in condition_results:
                condition_results[condition_key] = {'spectrograms': [], 'labels': []}
            
            if isinstance(value, np.ndarray):
                print(f"\nApplicazione STFT per '\033[1m{condition_key}\033[0m'\n")
                print(f"\033[1mShape\033[0m dei dati per \033[1m{condition_key}\033[0m: {value.shape}")
                
                all_trial_spectrograms = []

                # Itera su ogni trial
                for trial in range(value.shape[0]):
                    aggregated_channels = []  # Qui salveremo il vettore di frequenze per ciascun elettrodo
                    
                    # Itera su ogni canale (elettrodo)
                    for channel in range(value.shape[1]):
                        
                        # Estrai la porzione del segnale da analizzare (ad es. campioni da 50 a 300)
                        single_channel_data = value[trial, channel, 50:300]
                        
                        # Calcola la STFT per il canale corrente
                        f, t, Zxx = stft(single_channel_data, fs=fs, window='hann',
                                           nperseg=50, noverlap=25)
                        
                        # Calcola il modulo dello spettrogramma per avere valori reali
                        spect = np.abs(Zxx)
                        
                        # Aggrega lungo il tempo (axis=1) per ottenere un vettore di frequenze
                        aggregated = np.mean(spect, axis=1)  # shape: (n_frequencies,)
                        aggregated_channels.append(aggregated)
                    
                    # Converte la lista in array: shape iniziale (n_channels, n_frequencies)
                    aggregated_channels = np.array(aggregated_channels)
                    
                    # Trasponi in modo da avere:
                    # - asse y: frequenze (n_frequencies)
                    # - asse x: elettrodi (n_channels)
                    aggregated_image = aggregated_channels.T
                    all_trial_spectrograms.append(aggregated_image)

                # Salva tutti gli "immagini" ottenute per ogni trial della condizione corrente
                condition_results[condition_key]['spectrograms'].extend(all_trial_spectrograms)
                
                # Gestione delle etichette se presenti
                #if labels_key in data_dict:
                #    print(f"\nFound labels for condition \033[1m{labels_key}\033[0m, length: \033[1m{len(labels_key)}\033[0m\n")
                #    condition_results[condition_key]['labels'].extend(data_dict[labels_key])
                
                '''
                Modifiche specifiche:
                Riferimento corretto alla lunghezza delle etichette:

                Prima: len(labels_key) — Qui stavi misurando la lunghezza della chiave (che è una stringa come 'baseline_1_labels'), non dei dati associati.
                '''
                
                '''
                Ora: len(data_dict[labels_key]) — Ora la lunghezza è correttamente calcolata sui dati delle etichette, non sulla chiave.
                '''
                # Gestione delle etichette se presenti
                if labels_key in data_dict:
                    print(f"\nFound labels for condition \033[1m{labels_key}\033[0m, length: \033[1m{len(data_dict[labels_key])}\033[0m\n")
                    condition_results[condition_key]['labels'].extend(data_dict[labels_key])
                
            else:
                print(f"\033[1m{labels_key}\033[0m' non è un np.array, non applicare la STFT ")
    
    # Riorganizza i risultati in un dizionario finale
    all_subjects_condition_results = {}
    for condition_key, results in condition_results.items():
        if "_labels" in condition_key or len(results['spectrograms']) == 0:
            print(f"\nSkipping \033[1m{labels_key}\033[0m as it is a label or has no valid data.")
            continue
        
        wave_condition_name = f'spectrograms_{condition_key}'
        print(f"\n\nResults for \t\t\t\t\t\033[1m{wave_condition_name}\033[0m:\n\n")
        
        # Ora ogni trial produce un'immagine 2D di shape (n_frequencies, n_channels)
        
        spectrograms_3d = np.array(results['spectrograms'])
        all_subjects_condition_results[wave_condition_name] = {
            'spectrograms_3d': spectrograms_3d,
            'labels': results['labels']
        }
        print(f"spectrograms_3d shape for {wave_condition_name}: {spectrograms_3d.shape}")
    
    return all_subjects_condition_results


In [89]:
'''
CREAZIONE SPETTROGRAMMI ELETTRODI x FREQUENZE - VERSIONE UFFICIALE


Ti propongo una versione modificata della funzione che, per ogni soggetto e condizione, 
calcola la potenza spettrale tramite una FFT (usando np.fft.rfft) per ogni canale su un segmento specifico del segnale,
media i risultati sui trial e costruisce un’unica immagine 2D con:

Asse 0 (righe): vettore delle frequenze (ottenuto dalla FFT)
Asse 1 (colonne): elettrodi

In questo modo, per ogni soggetto e condizione avrai un’unica immagine in cui ogni “colonna” (cioè ogni elettrodo) 
mostra il vettore 1D delle potenze spettrali, come richiesto per poter interpretare successivamente il Grad-CAM.



Spiegazione delle modifiche

FFT anziché STFT:
Al posto di calcolare una STFT e poi aggregare nel tempo, ora per ogni canale si esegue una FFT sul segmento selezionato
(da segment_start a segment_end). La funzione np.fft.rfft restituisce solo i componenti a frequenza non negativa.

Aggregazione sui trial:

Per ciascun soggetto e condizione, 
i risultati della FFT ( = vettori di potenza spettrale), 
ossia il vettore ottenuto da ogni canale, viene impilato 
in modo da ottenere l'immagine di un trial. 
 
Ogni immagine rappresenta la potenza spettrale raccolta dalla FFT di ogni elettrodo di quel trial, e ogni immagine viene memorizzata separatamente.

Formazione dell’immagine:
I vettori di potenza di ciascun elettrodo vengono “impilati” in modo tale che, 
dopo la trasposizione, le righe rappresentino le frequenze e le colonne gli elettrodi. 

Questo formato permette al Grad-CAM di indicare quali frequenze e quali elettrodi risultano più discriminanti.

Questa funzione dovrebbe rispondere alle richieste del tuo supervisore, generando per ogni soggetto e condizione una sola immagine interpretabile con il Grad-CAM.


La funzione è stata progettata per rispettare quanto richiesto da Nicola. 

In particolare:

Calcolo per ogni elettrodo: Per ciascun canale (elettrodo) viene calcolata la FFT sul segmento specificato (da segment_start a segment_end), 
ottenendo un vettore 1D con la potenza spettrale in funzione della frequenza.

Aggregazione sui trial: 

Per ciascun soggetto e condizione, 
i risultati della FFT ( = vettori di potenza spettrale), 
ossia il vettore ottenuto da ogni canale, viene impilato 
in modo da ottenere l'immagine di un trial. 
 
Ogni immagine rappresenta la potenza spettrale raccolta dalla FFT di ogni elettrodo di quel trial, e ogni immagine viene memorizzata separatamente.

 
Creazione dell'immagine: 

Questi vettori, NON concatenati ma organizzati in colonne, vengono trasposti in modo da avere 

    - le righe rappresentanti le frequenze
    - le colonne gli elettrodi 
    
Così si ottiene, per ogni soggetto (e per ogni condizione) una singola immagine, 
che permette al Grad-CAM di evidenziare quali elettrodi (e quali frequenze) siano determinanti nel processo decisionale.

Se questo è esattamente quanto intendeva Nicola ("l'immagine sarebbe una sola per ogni soggetto" ottenuta raggruppando i vettori di ogni elettrodo), 
allora la funzione è adattata correttamente.


---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ----
RISULTATO FINALE:

1) Una immagine per ogni trial:
La variabile trial_power calcola la potenza spettrale per ciascun trial e la salva come una singola immagine (2D). 
    Queste immagini sono salvate nel dizionario condition_results[condition_key]['fft_images'] una per ciascun trial.

2) Shape dell'immagine:
Ogni immagine ha la forma (n_freq, n_channels), dove:

- n_freq è il numero di frequenze calcolato con np.fft.rfft.
- n_channels è il numero di elettrodi.

3) Etichette:
Se sono presenti le etichette per la condizione, vengono associate correttamente e stampate, come nel codice originale.

4) Dizionario finale:
Alla fine, il dizionario all_subjects_condition_results contiene un array 3D per ogni condizione (uno per ogni trial), con la forma 
    (n_trials, n_freq, n_channels).

Questo codice ora mantiene la logica originale di creare una immagine per ogni trial, mentre applica la FFT per calcolare la potenza spettrale. 

---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ---- ----

'''


import numpy as np

def create_spectrograms_from_fft_images_of_electrodes(data, segment_start = 50, segment_end = 300, fs = 250, max_freq_bins=45):
    
    """
    Per ogni soggetto e condizione, calcola le immagini della potenza spettrale per ciascun elettrodo 
    usando la FFT (np.fft.rfft) sul segmento definito del segnale (per esempio l'intero trial).
    
    Per ogni trial, viene calcolata la FFT per ogni canale, ottenendo un vettore 1D di potenza spettrale.
    Viene poi tagliato lo spettro per mantenere solo le prime 'max_freq_bins' frequenze.
    
    Ogni trial genera un'immagine 2D (righe: frequenze, colonne: elettrodi) che viene memorizzata separatamente.
    
    Parameters:
        data (list di dict): Ogni dict corrisponde a un soggetto e contiene le condizioni sperimentali
                              (chiavi con dati in formato np.array di shape (n_trials, n_channels, n_timepoints))
                              e, eventualmente, le relative etichette (con chiave condition_labels).
        segment_start (int): Indice iniziale del segmento da analizzare.
        segment_end (int): Indice finale del segmento da analizzare.
        fs (int): Frequenza di campionamento.
        max_freq_bins (int): Numero massimo di frequenze da mantenere (ad es. le prime 45 frequenze).
    
    Returns:
        dict: Un dizionario in cui per ogni condizione sono memorizzati:
              - 'spectrograms_3d': array 3D contenente le immagini per ogni trial (shape: n_trials x max_freq_bins x n_channels)
              - 'labels': etichette associate (se presenti)
    """
    
    import numpy as np


    # Dizionario per memorizzare i risultati per ciascuna condizione sperimentale
    condition_results = {}
    
    for idx, data_dict in enumerate(data):
        print(f"\n\n\t\t\t\t\t\033[1mProcessing Subject {idx + 1}\033[0m:\n")
        
        for condition, value in data_dict.items():
            
            # Gestione delle chiavi per condizioni e relative label
            if '_labels' in condition:
                base_condition = condition.replace('_labels', '')
                condition_key = base_condition
                labels_key = condition
            else:
                base_condition = condition
                condition_key = base_condition
                labels_key = f'{base_condition}_labels'
            
            # Inizializza la struttura per la condizione se non esiste
            if '_labels' not in condition and condition_key not in condition_results:
                condition_results[condition_key] = {'fft_images': [], 'labels': []}
            
            if isinstance(value, np.ndarray):
                print(f"\nApplicazione FFT per '\033[1m{condition_key}\033[0m'\n")
                print(f"\033[1mShape\033[0m dei dati per \033[1m{condition_key}\033[0m: {value.shape}")
                
                # Presupponiamo che 'value' abbia forma: (n_trials, n_channels, n_timepoints)
                n_trials, n_channels, _ = value.shape
                
                N = segment_end - segment_start  # lunghezza del segmento analizzato
                
                n_freq = N // 2 + 1  # np.fft.rfft restituisce n_freq = N//2 + 1
                
                # Determina il numero di frequenze da utilizzare (taglia lo spettro)
                effective_freq_bins = min(n_freq, max_freq_bins)
                
                # Itera su ogni trial e ogni canale per calcolare la potenza spettrale
                for trial in range(n_trials):
                    
                    #trial_power = np.zeros((n_channels, n_freq))  # Matrice per la potenza per ogni trial
                    trial_power = np.zeros((n_channels, effective_freq_bins))  # Matrice per la potenza per ogni trial
                    
                    for channel in range(n_channels):
                        
                        # Estrai il segmento del segnale
                        single_channel_data = value[trial, channel, segment_start:segment_end]
                        
                        # Calcola la FFT (solo componenti a frequenza non negativa)
                        # -> https://numpy.org/doc/stable/reference/generated/numpy.fft.rfft.html
                        fft_vals = np.fft.rfft(single_channel_data)
                        
                        # Calcola la potenza spettrale (modulo al quadrato)
                        power = np.abs(fft_vals) ** 2
                        #trial_power[channel] = power
                        trial_power[channel] = power[:effective_freq_bins]
                    
                    # Trasponi in modo che le righe siano le frequenze e le colonne gli elettrodi
                    fft_image = trial_power.T  # shape: (n_freq, n_channels)
                    #print(f"FFT image shape for trial {trial + 1} of condition '{condition_key}': {fft_image.shape}")
                    
                    # Salva l'immagine per il trial corrente
                    #Ogni trial genera una sua immagine della potenza spettrale che viene memorizzata separatamente!
                    condition_results[condition_key]['fft_images'].append(fft_image)
                
                # Gestione delle etichette se presenti
                if labels_key in data_dict:
                    print(f"\nFound labels for condition \033[1m{labels_key}\033[0m, length: \033[1m{len(data_dict[labels_key])}\033[0m\n")
                    condition_results[condition_key]['labels'].extend(data_dict[labels_key])
                
            else:
                print(f"\033[1m{labels_key}\033[0m non è un np.array, non applicare la FFT ")
    
    # Riorganizza i risultati in un dizionario finale
    all_subjects_condition_results = {}
    for condition_key, results in condition_results.items():
        if "_labels" in condition_key or len(results['fft_images']) == 0:
            print(f"\nSkipping \033[1m{condition_key}\033[0m as it is a label or has no valid data.")
            continue
        
        wave_condition_name = f'spectrograms_{condition_key}'
        print(f"\n\nResults for \t\t\t\t\t\033[1m{wave_condition_name}\033[0m:\n\n")
        
        # Ogni trial produce un'immagine 2D di shape (n_freq, n_channels)
        spectrograms_3d = np.array(results['fft_images'])
        all_subjects_condition_results[wave_condition_name] = {
            'spectrograms_3d': spectrograms_3d,
            'labels': results['labels']
        }
        print(f"spectrograms_3d shape for {wave_condition_name}: {spectrograms_3d.shape}")
    
    return all_subjects_condition_results


#new_all_subjects_condition_spectrograms_th = create_spectrograms_from_fft_images_of_electrodes (therapists_data, segment_start = 50, segment_end = 300, fs=250, max_freq_bins=45)

In [ ]:
# Richiamo della funzione per processare tutti i soggetti e ottenere i risultati per ciascuna condizione
#new_all_subjects_condition_spectrograms_pt = create_spectograms_from_stft_electrode_freq (patients_data, window_size  = 50, step_size = 25, fs=250)

In [ ]:
# Richiamo della funzione per processare tutti i soggetti e ottenere i risultati per ciascuna condizione
#new_all_subjects_condition_spectrograms_pt = create_spectograms_from_stft(patients_data, window_size=50, step_size=25, fs=250)

In [90]:
new_all_subjects_condition_spectrograms_pt = create_spectrograms_from_fft_images_of_electrodes (patients_data, segment_start = 50, segment_end = 300, fs=250, max_freq_bins=45)



					Processing Subject 1:


Applicazione FFT per 'baseline_1'

Shape dei dati per baseline_1: (44, 61, 300)

Found labels for condition baseline_1_labels, length: 44


Applicazione FFT per 'th_resp_1'

Shape dei dati per th_resp_1: (40, 61, 300)

Found labels for condition th_resp_1_labels, length: 40


Applicazione FFT per 'pt_resp_1'

Shape dei dati per pt_resp_1: (43, 61, 300)

Found labels for condition pt_resp_1_labels, length: 43


Applicazione FFT per 'shared_resp_1'

Shape dei dati per shared_resp_1: (47, 61, 300)

Found labels for condition shared_resp_1_labels, length: 47

baseline_1_labels non è un np.array, non applicare la FFT 
th_resp_1_labels non è un np.array, non applicare la FFT 
pt_resp_1_labels non è un np.array, non applicare la FFT 
shared_resp_1_labels non è un np.array, non applicare la FFT 


					Processing Subject 2:


Applicazione FFT per 'baseline_2'

Shape dei dati per baseline_2: (60, 61, 300)

Found labels for condition baseline_2_labels, length: 60



In [91]:
print('finito')

finito


In [92]:
new_all_subjects_condition_spectrograms_pt.keys()

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [93]:
new_all_subjects_condition_spectrograms_pt['spectrograms_baseline_1'].keys()

dict_keys(['spectrograms_3d', 'labels'])

In [94]:
#new_all_subjects_condition_spectrograms_pt['spectrograms_baseline_1']['spectrograms_4d'].shape

new_all_subjects_condition_spectrograms_pt['spectrograms_baseline_1']['spectrograms_3d'].shape

(44, 45, 61)

In [95]:
#Salvo ricostruzioni 4° e 5° livello terapisti

'''PATH  --> cd Plots_Sliding_Estimator_MNE'''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('all_subjects_condition_results_th.pkl', 'wb') as f:
#    pickle.dump(all_subjects_condition_results_th, f)
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'


import pickle

# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_all_subjects_condition_spectrograms_pt_2D.pkl', 'wb') as f:
    pickle.dump(new_all_subjects_condition_spectrograms_pt, f)

#### Esempi di Plots da Un Trial, Una Condizionizione Sperimentale, Un Canale EEG

In [ ]:
'''
Il tempo che vedi nell'asse X non è espresso direttamente in termini di punti EEG, 
ma nel dominio delle finestre scorrevoli (che sono di 75 punti con uno shift di 25 punti).


Questo codice  considera l'inizio della finestra STFT come riferimento per il tempo.
'''

import matplotlib.pyplot as plt

# Estrarre il primo soggetto e la prima condizione
first_condition_key = list(new_all_subjects_condition_spectrograms_pt.keys())[0]
spectrograms = new_all_subjects_condition_spectrograms_pt[first_condition_key]['spectrograms_4d']

# Selezionare il primo trial e il primo canale
trial_index = 0
channel_index = 0
spectrogram = np.abs(spectrograms[trial_index, channel_index, :, :])  # Prendere il modulo dello spettrogramma

# Ricavare frequenze e intervalli temporali dalla STFT
fs = 250  # Frequenza di campionamento EEG
window_size = 75
step_size = 25

f, t = np.linspace(0, fs / 2, spectrogram.shape[0]), np.arange(spectrogram.shape[1])  # Indici di tempo grezzi

# Convertire gli intervalli temporali da campioni EEG a millisecondi
t_ms = -200 + (t * step_size * (1000 / fs))  # -200 ms è il tempo di prestimolo iniziale

# Creare il plot
plt.figure(figsize=(10, 6))
plt.pcolormesh(t_ms, f, spectrogram, shading='auto', cmap='jet')
plt.colorbar(label='Amplitude')
plt.xlabel('Time (ms)')
plt.ylabel('Frequency (Hz)')
plt.title(f'Spectrogram - {first_condition_key} - Trial {trial_index+1} - Channel {channel_index+1}')
plt.axvline(0, color='k', linestyle='--', label="Stimulus onset")
plt.legend()
plt.show()


In [ ]:
'''

Questo Codice considera il centro della finestra come riferimento.
Ossia, è più rappresentativo rispetto alla stft di ogni finestra in sostanza, 
cioè fornisce una visualizzazione migliore delle componenti frequenziali del segnale in funzione di quella finestra per cui è stata fatta la stft?


Perché è più corretto?
Quando calcoli la STFT, la trasformata viene effettuata su una finestra mobile di lunghezza window_size (75 campioni). 
Il risultato della STFT rappresenta il contenuto in frequenza della finestra nel suo complesso, non solo il punto iniziale della finestra.

Nel Codice 1, il tempo è allineato con l'inizio della finestra, il che può dare un’impressione leggermente distorta:

La STFT a t = -200 ms viene plottata come se rappresentasse solo il segnale in quel momento, ma in realtà include informazioni da -200 ms a -100 ms.
Nel Codice 2, invece, il tempo è allineato con il centro della finestra, il che è più rappresentativo:

La STFT calcolata sulla finestra [-200, -100] ms viene plottata a t = -150 ms, che è il centro effettivo della finestra.
Vantaggi della rappresentazione nel Codice 2
✅ Ogni punto temporale dello spettrogramma mostra il contenuto in frequenza della finestra corrispondente, e non di un singolo istante.
✅ La rappresentazione è più coerente con l’effettivo contributo temporale delle finestre, migliorando la leggibilità.
✅ Se si vuole confrontare i risultati con altri metodi di analisi nel dominio del tempo (es. ERP), questa rappresentazione è più affidabile.

📌 Conclusione:
Sì, il Codice 2 fornisce una visualizzazione più accurata delle componenti frequenziali di ogni finestra STFT, 
perché mostra i risultati nel punto temporale più rappresentativo per ogni finestra.


'''

import matplotlib.pyplot as plt
import numpy as np

# Seleziona la prima condizione sperimentale
first_condition = list(new_all_subjects_condition_spectrograms_pt.keys())[0]

# Estrai gli spettrogrammi per la condizione selezionata
spectrograms_4d = new_all_subjects_condition_spectrograms_pt[first_condition]['spectrograms_4d']

# Seleziona il primo trial e il primo canale
trial_idx = 0
channel_idx = 0
spectrogram_trial_channel = np.abs(spectrograms_4d[trial_idx, channel_idx, :, :])  # Modulo della STFT

# Definizione dei parametri
fs = 250  # Frequenza di campionamento (Hz)
window_size = 75  # Lunghezza della finestra STFT (punti EEG)
step_size = 25  # Spostamento tra finestre (punti EEG)

# Crea asse delle frequenze e del tempo in ms
frequencies = np.linspace(0, fs / 2, spectrogram_trial_channel.shape[0])  # Frequenze in Hz
time_points = ((np.arange(spectrogram_trial_channel.shape[1]) * step_size) + (window_size // 2)) * 4 - 200  # Tempo in ms

# Plot dello spettrogramma
plt.figure(figsize=(10, 6))
plt.pcolormesh(time_points, frequencies, spectrogram_trial_channel, shading='auto', cmap='jet')
plt.colorbar(label='Magnitudine')
plt.xlabel('Tempo (ms)')
plt.ylabel('Frequenza (Hz)')
plt.axvline(x=0, color='k', linestyle='--', label='Stimolo')  # Linea verticale sullo stimolo
plt.title(f'Spettrogramma - {first_condition} (Trial {trial_idx+1}, Canale {channel_idx+1})')
plt.legend()
plt.show()


#### **Concatenazione** All **SINGLE** Subject **Spectrograms (PT)** per **Tutte le Condizioni Sperimentali**

In [96]:
new_all_subjects_condition_spectrograms_pt.keys()

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [97]:
import numpy as np

'''TOLGO PER SPETTROGRAMMI FREQUENZE x ELETTRODI'''
#selected_channels = [12, 30, 48]  # Indici per Fz, Cz, Pz

# Creazione di un dizionario dei dati di tutti i terapisti singolarmente, per salvare gli spettrogrammi calcolati
new_single_pt_all_extracted_spectrograms_2D = {}

# Iterazione su tutte le condizioni sperimentali di tutti i soggetti 

for condition, data in new_all_subjects_condition_spectrograms_pt.items():
    
    # Estrarre le etichette per la condizione corrente
    labels = data['labels']
    
    '''TOLGO PER SPETTROGRAMMI FREQUENZE x ELETTRODI'''
    #spectrograms = data['spectrograms_4d']
    
    spectrograms = data['spectrograms_3d']
    
    '''TOLGO PER SPETTROGRAMMI FREQUENZE x ELETTRODI'''
    #Selezione dei canali di interesse (Fz, Cz e Pz)
    #spectrograms = spectrograms[:, selected_channels, :, :]
    
    new_single_pt_all_extracted_spectrograms_2D[condition] = {
        'spectrograms': spectrograms,
        #'delta': delta_reconstruction,
        #'coeff_fifth_detail_theta': coeff_fifth_detail_theta, 
        'labels': labels
    }
    
# Verifica delle dimensioni del risultato estratto per una condizione specifica di ogni soggetto
print(f"\t\t\033[1mEstrazione Spettrogrammi di tutti i terapisti per tutte le condizioni sperimentali")
print(f"\n\n\t\t\t\t(i.e., \033[1mnew_single_th_all_extracted_spectrograms_2D\033[0m):\n")

for condition, extracted_data in new_single_pt_all_extracted_spectrograms_2D.items():
    
    print(f"Condizione: \033[1m{condition}\033[0m, "
          f"Spectrograms shape: \033[1m{extracted_data['spectrograms'].shape}\033[0m, "
          f"Labels: \033[1m{len(extracted_data['labels'])}\033[0m")


		Estrazione Spettrogrammi di tutti i terapisti per tutte le condizioni sperimentali


				(i.e., new_single_th_all_extracted_spectrograms_2D):

Condizione: spectrograms_baseline_1, Spectrograms shape: (44, 45, 61), Labels: 44
Condizione: spectrograms_th_resp_1, Spectrograms shape: (40, 45, 61), Labels: 40
Condizione: spectrograms_pt_resp_1, Spectrograms shape: (43, 45, 61), Labels: 43
Condizione: spectrograms_shared_resp_1, Spectrograms shape: (47, 45, 61), Labels: 47
Condizione: spectrograms_baseline_2, Spectrograms shape: (60, 45, 61), Labels: 60
Condizione: spectrograms_th_resp_2, Spectrograms shape: (40, 45, 61), Labels: 40
Condizione: spectrograms_pt_resp_2, Spectrograms shape: (43, 45, 61), Labels: 43
Condizione: spectrograms_shared_resp_2, Spectrograms shape: (61, 45, 61), Labels: 61
Condizione: spectrograms_baseline_3, Spectrograms shape: (57, 45, 61), Labels: 57
Condizione: spectrograms_th_resp_3, Spectrograms shape: (40, 45, 61), Labels: 40
Condizione: spectrograms_pt_resp_3

In [98]:
'''Salvataggio di new_single_th_all_extracted_spectrograms_2D'''

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

import pickle

# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_single_pt_all_extracted_spectrograms_2D.pkl', 'wb') as f:
    pickle.dump(new_single_pt_all_extracted_spectrograms_2D, f)

In [99]:
new_single_pt_all_extracted_spectrograms_2D.keys()

new_single_pt_all_extracted_spectrograms_2D['spectrograms_baseline_1'].keys()

dict_keys(['spectrograms', 'labels'])

In [100]:
'''
Questa struttura consente di avere i dati degli spettrogrammi correttamente organizzati e concatenati per ogni soggetto,
mantenendo la corrispondenza tra dati e etichette per ogni condizione sperimentale

Da           "single_th_all_extracted_reconstructions"       a           "subject_level_concatenations_th"

Da           "new_single_th_all_extracted_reconstructions"       a       "new_subject_level_concatenations_th"

Da           "new_single_th_all_extracted_spectrograms_2D"       a       "new_subject_level_concatenations_spectrograms_th_2D"
'''


# Dizionario per contenere i dati concatenati per ogni soggetto
new_subject_level_concatenations_spectrograms_pt_2D = {}

# Variabile per tracciare il soggetto precedente
previous_subject_suffix = None

print(f"\t\t\033[1mConcatenazione spettrogrammi 2D per OGNI soggetto di TUTTE le condizioni sperimentali INSIEME\033[0m")

# Iterazione su tutte le chiavi di new_single_th_all_extracted_spectrograms_2D
for condition, data in new_single_pt_all_extracted_spectrograms_2D.items():
    
    # Estrazione del suffisso numerico del soggetto
    subject_suffix = condition.split('_')[-1]  # Prende solo la parte numerica
    
    # Creazione del nome della chiave del soggetto specifico
    subj_name = f'pt_{subject_suffix}'
    
    # Se stiamo per passare a un nuovo soggetto, concatenare e stampare i risultati del soggetto precedente
    if previous_subject_suffix is not None and subject_suffix != previous_subject_suffix:
        
        print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('pt_{previous_subject_suffix}'):\033[0m\n")
        prev_subject_name = f'pt_{previous_subject_suffix}'
        levels = new_subject_level_concatenations_spectrograms_pt_2D[prev_subject_name]

        # Concatenazione dei dati prima della stampa
        spectrograms_concat = np.concatenate(levels['spectrograms'], axis=0)
        labels_concat = np.concatenate(levels['labels'], axis=0)

        print(f"Soggetto: \033[1m{prev_subject_name}\033[0m, "
              f"Spettrogrammi shape: \033[1m{spectrograms_concat.shape}\033[0m, "
              f"Labels length: \033[1m{len(labels_concat)}\033[0m")
        
        # Salvataggio dei dati concatenati nel dizionario
        new_subject_level_concatenations_spectrograms_pt_2D[prev_subject_name]['spectrograms'] = spectrograms_concat
        new_subject_level_concatenations_spectrograms_pt_2D[prev_subject_name]['labels'] = labels_concat
    
    # Inizializzare il dizionario per il soggetto specifico se non esiste già
    if subj_name not in new_subject_level_concatenations_spectrograms_pt_2D:
        new_subject_level_concatenations_spectrograms_pt_2D[subj_name] = {
            'spectrograms': [],
            'labels': []
        }
    
    # Stampiamo le informazioni per ogni condizione
    print(f"\n\n\nSoggetto: \033[1m{subj_name}\033[0m, Condizione: \033[1m{condition}\033[0m")
    print(f"  - Spettrogrammi shape: \033[1m{data['spectrograms'].shape}\033[0m")
    print(f"  - Labels shape: \033[1m{len(data['labels'])}\033[0m")
    print(f"  - Valore unico delle etichette: \033[1m{np.unique(data['labels'])}\033[0m")
    
    # Concatenazione dei dati
    new_subject_level_concatenations_spectrograms_pt_2D[subj_name]['spectrograms'].append(data['spectrograms'])
    new_subject_level_concatenations_spectrograms_pt_2D[subj_name]['labels'].append(data['labels'])
    
    # Aggiorna il soggetto precedente
    previous_subject_suffix = subject_suffix

# Dopo aver iterato su tutte le condizioni, concatenare e stampare le informazioni dell'ultimo soggetto
if previous_subject_suffix is not None:
    
    last_subject_name = f'pt_{previous_subject_suffix}'
    levels = new_subject_level_concatenations_spectrograms_pt_2D[last_subject_name]
    
    print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('{last_subject_name}'):\033[0m\n")
    
    # Concatenazione dei dati dell'ultimo soggetto
    spectrograms_concat = np.concatenate(levels['spectrograms'], axis=0)
    labels_concat = np.concatenate(levels['labels'], axis=0)
    
    # Salvataggio dei dati concatenati dell'ultimo soggetto nel dizionario
    new_subject_level_concatenations_spectrograms_pt_2D[last_subject_name] = {
        'spectrograms': spectrograms_concat,
        'labels': labels_concat
    }
    
    print(f"Soggetto: \033[1m{last_subject_name}\033[0m, "
          f"Spettrogrammi shape: \033[1m{spectrograms_concat.shape}\033[0m, "
          f"Labels length: \033[1m{len(labels_concat)}\033[0m\n\n")


		Concatenazione spettrogrammi 2D per OGNI soggetto di TUTTE le condizioni sperimentali INSIEME



Soggetto: pt_1, Condizione: spectrograms_baseline_1
  - Spettrogrammi shape: (44, 45, 61)
  - Labels shape: 44
  - Valore unico delle etichette: ['0']



Soggetto: pt_1, Condizione: spectrograms_th_resp_1
  - Spettrogrammi shape: (40, 45, 61)
  - Labels shape: 40
  - Valore unico delle etichette: ['1']



Soggetto: pt_1, Condizione: spectrograms_pt_resp_1
  - Spettrogrammi shape: (43, 45, 61)
  - Labels shape: 43
  - Valore unico delle etichette: ['2']



Soggetto: pt_1, Condizione: spectrograms_shared_resp_1
  - Spettrogrammi shape: (47, 45, 61)
  - Labels shape: 47
  - Valore unico delle etichette: ['3']


				Concatenazioni per il soggetto corrente ('pt_1'):

Soggetto: pt_1, Spettrogrammi shape: (174, 45, 61), Labels length: 174



Soggetto: pt_2, Condizione: spectrograms_baseline_2
  - Spettrogrammi shape: (60, 45, 61)
  - Labels shape: 60
  - Valore unico delle etichette: ['0']



So

In [101]:
'''CHIAVI DI TUTTO IL DIZIONARIO '''
#subject_level_concatenations_th.keys()


new_subject_level_concatenations_spectrograms_pt_2D.keys()


#SOGGETTO 1

#CHIAVI
#subject_level_concatenations_th['th_1'].keys()

#DATI
#subject_level_concatenations_th['th_1']['theta'].shape

#new_subject_level_concatenations_th['th_1']['theta'].shape

#subject_level_concatenations_th['th_1']['delta'].shape

#LABELS
#subject_level_concatenations_th['th_1']['labels'].shape)
#type(subject_level_concatenations_th['th_1']['labels'])

# Check della concantenazione delle labels TH_1

#subject_level_concatenations_th['th_1']['labels'][:42]
#subject_level_concatenations_th['th_1']['labels'][41:81]
#subject_level_concatenations_th['th_1']['labels'][81:120]
#subject_level_concatenations_th['th_1']['labels'][121:164]

dict_keys(['pt_1', 'pt_2', 'pt_3', 'pt_4', 'pt_5', 'pt_6', 'pt_7', 'pt_8', 'pt_9', 'pt_10', 'pt_11', 'pt_12', 'pt_13', 'pt_14', 'pt_15', 'pt_16', 'pt_17', 'pt_18', 'pt_19', 'pt_20'])

In [102]:
new_subject_level_concatenations_spectrograms_pt_2D['pt_1'].keys()



dict_keys(['spectrograms', 'labels'])

In [103]:
#subject_level_concatenations_th['th_15']['labels'].shape

In [104]:
#subject_level_concatenations_th['th_1'].keys()

new_subject_level_concatenations_spectrograms_pt_2D['pt_1']['spectrograms'].shape


(174, 45, 61)

In [105]:
#unique_values, counts = np.unique(subject_level_concatenations_th['th_1']['labels'], return_counts=True)

#unique_values, counts = np.unique(new_subject_level_concatenations_th['th_1']['labels'], return_counts=True)

In [106]:
#unique_values
#counts
#counts[0]

In [107]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [108]:
#Salvo ricostruzioni 4° e 5° livello per singolo terapista con concatenazioni dati e labels 

''' PATH  --> cd Plots_Sliding_Estimator_MNE '''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('subject_level_concatenations_pt.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations_pt, f)
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_1_45 '''

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

import pickle

# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_subject_level_concatenations_spectrograms_pt_2D.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_spectrograms_pt_2D, f)

#### **Concatenazione** All **SINGLE** Subject **Spectrograms (PT)** per **Coppie di Condizioni Sperimentali**

In [109]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [110]:
cd ..

/home/stefano/Interrogait


In [111]:
cd New_Plots_Sliding_Estimator_MNE_1_45/

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [112]:
import pickle
import numpy as np

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_single_pt_all_extracted_spectrograms_2D.pkl', 'rb') as f:
    new_single_pt_all_extracted_spectrograms_2D = pickle.load(f)

In [113]:
new_single_pt_all_extracted_spectrograms_2D.keys()

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [114]:
new_single_pt_all_extracted_spectrograms_2D['spectrograms_baseline_1'].keys()

dict_keys(['spectrograms', 'labels'])

##### Spiegazione STEP - Concatenazione All Single Subject Spectrograms (TH) across Couples of Experimental Conditions

###### **Concatenazione All Single Subject Data (TH) per Coppie di Condizioni Sperimentali**

<br>

In questo caso, voglio **trasformare le variabili che contengono i miei dati e labels delle 4 condizioni sperimentali assieme**, in modo **da creare sottoinsiemi per ogni possibile coppia di condizioni sperimentali**. 

Dunque quello che si dovrà fare **per ogni coppia**:

1) **Filtrare i dati e le etichette**:

- **Estrarre** i dati associati **SOLO alle DUE condizioni in esame** (ad esempio 0 e 1, oppure 1 e 2).
- **Creare un nuovo array di etichette** e **un array di dati** ***corrispondenti*** **SOLO a quelle DUE condizioni**.

2) **Ripetere questa operazione per OGNI combinazione**:

- **Assicurarsi di considerare tutte le coppie** di condizioni sperimentali **SENZA ripetizioni** (ad esempio, non serve processare sia 0 vs 1 che 1 vs 0, perché sono equivalenti!).

3) **Creare quindi una struttura organizzata**, che contenga i dati e le etichette separatamente per ogni coppia, per ciascun livello di ricostruzione (theta, delta, theta_strict).

<br>

Quindi l'obiettivo è di modificare la procedura in modo da **concatenare SOLO le coppie di condizioni sperimentali per OGNI soggetto**. 

Per fare questo, possiamo utilizzare un **approccio combinatorio** per generare **tutte le possibili coppie di condizioni**.


Per quanto riguarda il calcolo combinatorio, possiamo usare il concetto di combinazioni per selezionare le coppie. 
Se hai 4 condizioni, il numero di combinazioni di coppie di condizioni (senza ripetizioni) si calcola come:

$$
\binom{4}{2} = \frac{4!}{2!(4-2)!} = 6
$$


Quindi, con 4 condizioni sperimentali, le combinazioni di coppie di condizioni saranno 6, e queste coppie sono:

(condizione 1, condizione 2) = 'baseline vs th_resp'
(condizione 1, condizione 3) = 'baseline vs pt_resp'
(condizione 1, condizione 4) = 'baseline vs shared_resp'
(condizione 2, condizione 3) = 'th_resp vs pt_resp'
(condizione 2, condizione 4) = 'th_resp vs shared_resp'
(condizione 3, condizione 4) = 'pt_resp vs shared_resp' 


<br>

Piano di modifiche al codice:

1) **Creazione delle coppie di condizioni**: Per ogni soggetto, genereremo tutte le coppie possibili di condizioni sperimentali. Utilizzeremo itertools.combinations per ottenere queste coppie.

2) **Concatenazione per ciascuna coppia**: Per ogni coppia di condizioni, concatenare i dati e le etichette delle due condizioni selezionate.

3) **Salvataggio delle concatenazioni**: Creeremo un dizionario per ciascuna coppia di condizioni per ogni soggetto.


**N.B.**

Nel codice che sto creando...

Ho fatto in modo che ci sia il modo di capire, **per ogni coppia di condizione sperimentale di dati e labels**, a quali condizione sperimentali di dati e labels ci si riferisca, mi spiego:

Sviluppo un **modo "standardizzato" per il quale per OGNI coppia di condizione sperimentale, la variabile che conterrà i dati e labels associate, sia chiamata in un certo modo**...

E nello specifico **con il nome delle DUE condizioni sperimentali che conterranno quei dati e relative labels**...

Del tipo: 

- se è baseline vs th_resp, la variabile sarà "baseline_vs_th_resp"
- se è baseline vs pt_resp, la variabile sarà "baseline_vs_pt_resp"
- se è baseline vs shared_resp, la variabile sarà "baseline_vs_shared_resp"


Senza contare che, questo **processo di standardizzazione del nome delle variabili**, deve esser fatto **per ogni livello di ricostruzione dei dati (sia 4° e 5° livello a partire dai coefficienti di approssimazione, che dal 5 ° livello dei coefficienti di dettaglio)**..

Questo significherebbe che, **per ogni soggetto**, dovrei (o potrei insomma) creare **un dizionario**, che 

- Contenga delle **sotto-chiavi di secondo ordine** (che son theta, delta e theta_strict) e dentro ognuna di queste
- Ci siano contenute **le relative 6 sotto-sotto-chiavi di terzo ordine**, relative ai dati e alle labels associate (anch'esse concatenate ovviamente) delle diverse combinazioni di condizioni sperimentali...


Ossia, vogliamo creare un dizionario strutturato che rappresenti ogni combinazione di coppie di condizioni sperimentali per ciascun soggetto, separando i dati e le etichette per i vari livelli di ricostruzione (theta, delta, theta_strict). 

Ogni combinazione di condizioni sperimentali sarà memorizzata in una chiave strutturata, come ad esempio "baseline_vs_th_resp", e all'interno di ciascuna chiave avremo le informazioni per i vari livelli di ricostruzione.


<br>


#### Esempio di Struttura proposta per il dizionario:


- Soggetto: ad esempio "th_1".
- Livelli di ricostruzione: theta, delta, theta_strict.
- Combinazioni di condizioni sperimentali: per ciascun livello di ricostruzione, avremo sotto-chiavi per ogni coppia di condizioni.

        new_subject_level_concatenations = {
            'th_1': {
                'theta': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                },
                'delta': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                },
                'theta_strict': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                }
            }
        }

<br>

**SOTTO-STEP 1: IDENTIFICAZIONE DELLE STRINGA NUMERICHE PER LA CREAZIONE DELLE VARIABILI - FUTURE CHIAVI - CHE CONTENGONO LE COPPIE DI DATI E LABELS DELLE RELATIVE COPPIE DI CONDIZIONI SPERIMENTALI CONSIDERATE NEL CICLO CORRENTE DEL LOOP**

Aspetta, ci sono altre cose che dovrebbero esser integrate nel codice...

cominciamo dalla prima, che è relativa all' "inferire" diciamo il nome da fornire alla variabile che conterrà i dati e labels delle due condizioni sperimentali correnti... e deve esser fatto, a partire dal nome delle chiavi di 

"new_single_th_all_extracted_reconstructions"...

ora, le sue chiavi son queste

dict_keys(['wave_baseline_1', 'wave_th_resp_1', 'wave_pt_resp_1', 'wave_shared_resp_1', 'wave_baseline_2', 'wave_th_resp_2', 'wave_pt_resp_2', 'wave_shared_resp_2', 'wave_baseline_3', 'wave_th_resp_3', 'wave_pt_resp_3', 'wave_shared_resp_3', 'wave_baseline_4', 'wave_th_resp_4', 'wave_pt_resp_4', 'wave_shared_resp_4', 'wave_baseline_5', 'wave_th_resp_5', 'wave_pt_resp_5', 'wave_shared_resp_5', 'wave_baseline_6', 'wave_th_resp_6', 'wave_pt_resp_6', 'wave_shared_resp_6', 'wave_baseline_7', 'wave_th_resp_7', 'wave_pt_resp_7', 'wave_shared_resp_7', 'wave_baseline_8', 'wave_th_resp_8', 'wave_pt_resp_8', 'wave_shared_resp_8', 'wave_baseline_9', 'wave_th_resp_9', 'wave_pt_resp_9', 'wave_shared_resp_9', 'wave_baseline_10', 'wave_th_resp_10', 'wave_pt_resp_10', 'wave_shared_resp_10', 'wave_baseline_11', 'wave_th_resp_11', 'wave_pt_resp_11', 'wave_shared_resp_11', 'wave_baseline_12', 'wave_th_resp_12', 'wave_pt_resp_12', 'wave_shared_resp_12'])


ora, il modo in cui si identifica un certo soggetto (ossia la chiavi di "primo ordine" che indentificano il soggetto, ossia ad esempio 'th_1'), dipenderebbe dal numero stringa che c'è alla fine di ogni nome stringa di ogni chiave dentro "new_single_th_all_extracted_reconstructions", mi spiego:

il codice dovrebbe capire che, ad esempio, solo l'ultima carattere stringa di queste prime 4 chiavi:

'wave_baseline_1', 'wave_th_resp_1', 'wave_pt_resp_1', 'wave_shared_resp_1', 

si riferisca al soggetto 1, ossia al futuro "th_1"...


per il soggetto 2, sarebbero: 

'wave_th_resp_2', 'wave_pt_resp_2', 'wave_shared_resp_2', e così via per gli altri soggetti..


Facendo attenzione al fatto che, dopo il soggetto 9, ovviamente, si passerà alle decine (a livello numerico), per cui saranno gli ultime due caratteri da considerare per l'identificazione delle sue rispettive chiavi, che in quel caso saranno per il soggetto 10, ossia il futuro th_10

'wave_baseline_10', 'wave_th_resp_10', 'wave_pt_resp_10', 'wave_shared_resp_10',

Inoltre, poi, per creare le variabili associate alle coppie di dati e labels delle relative condizioni sperimentali, dovrà il codice far in modo che il nome di quella variabile dipenda dalle stringhe sempre che si riferiscono al nome delle due chiavi di "new_single_th_all_extracted_reconstructions" da cui preleva i dati e le labels... 

ad esempio, se deve creare la variabile dei dati 'baseline_vs_th_resp" del primo soggetto, le chiavi rispettive da cui deve andare a prelevare le stringhe saranno appunto "'wave_baseline_1'" e "'wave_th_resp_1'"....

diciamo che si potrebbe creare una lista di stringhe che sarà del tipo:

experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp'], per vedere se una di queste sia dentro la rispettiva chiave di  new_single_th_all_extracted_reconstructions su cui sta iterando, che nel nostro caso di esempio sarebbero sempre

'wave_baseline_1' (e da cui vede che c'è la stinga 'baseline')
'wave_th_resp_1' (e da cui vede che c'è la stinga 'th_resp')

è chiaro?


<br>

In sostanza, desideri un modo per inferire dinamicamente il nome del soggetto e delle variabili che conterranno i dati e le etichette per ogni combinazione di condizioni, a partire dal nome delle chiavi di new_single_th_all_extracted_reconstructions. Ecco un piano per raggiungere questo obiettivo:

Passaggi:

- Identificare il soggetto:

Le chiavi di new_single_th_all_extracted_reconstructions finiscono con un numero che identifica il soggetto (es. wave_baseline_1, wave_th_resp_1, wave_pt_resp_1).
Questo numero può essere estratto dalle ultime cifre della chiave (ad esempio, 1 da wave_baseline_1).
La variabile associata a ciascun soggetto sarà chiamata th_X, dove X è il numero del soggetto.

- Generare dinamicamente il nome delle variabili:

A partire dai nomi delle chiavi, possiamo inferire quale combinazione di condizioni sperimentali stiamo trattando (es. baseline_vs_th_resp).
Creeremo una lista delle condizioni (experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']), quindi esamineremo le chiavi per determinare quali condizioni sono presenti.

- Creare il dizionario:

A ciascun soggetto verrà associato un dizionario, e per ogni combinazione di condizioni sperimentali, assoceremo i dati e le etichette in una chiave che seguirà la convenzione del tipo baseline_vs_th_resp.


<br>

Spiegazione:

1) Estrazione delle condizioni e soggetto:

La chiave, ad esempio wave_baseline_1, viene separata in parti. La parte baseline viene estratta per determinare la condizione, mentre 1 indica il numero del soggetto.
Queste informazioni vengono utilizzate per creare il nome del soggetto, th_1.

2) Combinazioni di condizioni:

La lista experimental_conditions contiene le 4 condizioni: baseline, th_resp, pt_resp, shared_resp.
Per ogni soggetto, controlliamo quali condizioni sono disponibili nella chiave (ad esempio, se il soggetto 1 ha wave_baseline_1 e wave_th_resp_1, creiamo la combinazione baseline_vs_th_resp).

3) Creazione dinamica delle variabili:

Utilizziamo la combinazione di condizioni per generare la chiave della variabile (baseline_vs_th_resp).
I dati e le etichette per la combinazione di condizioni vengono estratti e concatenati.


4) Risultato finale:

La struttura finale del dizionario new_subject_level_concatenations avrà una chiave per ciascun soggetto (th_1, th_2, ecc.), e sotto ogni soggetto ci saranno le combinazioni di condizioni per ciascun livello di ricostruzione (theta, delta, theta_strict), con i dati e le etichette corrispondenti.

<br>

Esempio di output:

    {
        'th_1': {
            'theta': {
                'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'th_resp_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                # Altre combinazioni...
            },
            'delta': {
                # Stessa struttura per 'delta'
            },
            'theta_strict': {
                # Stessa struttura per 'theta_strict'
            }
        }
    }

 
Questa struttura ti permetterà di avere un'organizzazione chiara e dinamica dei dati per ogni soggetto e combinazione di condizioni sperimentali.
 
 
<br>

**SOTTO-STEP 2: IDENTIFICAZIONE DELLE STRINGA ALFABETICHE PER LA CREAZIONE DELLE VARIABILI - FUTURE CHIAVI - CHE CONTENGONO IL NOME DELLE DUE COPPIE DI CONDIZIONI SPERIMENTALI DI CUI VENGONO PRELEVATI I DATI E LABELS CONCATENATI E CHE VENGONON CONSIDERATE NEL CICLO CORRENTE DEL LOOP**


ok, ora c'è una ultima cosa che mi manca da dirti, che è relativa alla ri-assegnazione del codice numerico associato ad ogni coppia di condizioni sperimentali...

nel senso che, originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò 

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo


print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n")
print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n")
print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n")
print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")


Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza,  nel tuo codice, ho bisogno che 

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre 

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e  e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare le labels andranno ovviamente riconvertite! Perché?
perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempip, in quel caso, le sue labels (che son  originariamente codificate come '1' in 'new_subject_level_concatenations'!) diveteranno '0', mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...


è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?


<br>

La **logica di ri-assegnazione delle etichette (labels)** è chiara e posso integrarla nel codice. 

La logica che stai descrivendo consiste essenzialmente nel **garantire che, quando crei una variabile che contiene dati e etichette per due condizioni sperimentali, le etichette siano sempre "0" per la prima condizione (cond_1) e "1" per la seconda condizione (cond_2)**, 

                **INDIPENDENTEMENTE** da come sono originariamente codificate in **"new_single_th_all_extracted_reconstructions"!
                
                

Ecco come possiamo procedere:

- Identificazione delle condizioni: Come hai descritto, determineremo le due condizioni sperimentali da confrontare, ad esempio "baseline" contro "th_resp", "baseline" contro "pt_resp", ecc.

- Riconversione delle etichette:

 - Se la condizione di confronto è "baseline" (che è associata a 0), non dobbiamo modificare le etichette.
 - Se la condizione di confronto non è "baseline", dovremo riconvertire le etichette di quella condizione a 0 e le etichette della condizione di confronto a 1.

- Struttura del codice: Durante la creazione delle variabili, dovremo controllare quale condizione è la prima (cond_1) e quale è la seconda (cond_2), e applicare questa logica per ri-assegnare le etichette di conseguenza.


<br>

Inoltre


dentro 

"# Crea tutte le combinazioni uniche di condizioni sperimentali (es. 'baseline vs th_resp')
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
"

Effettivamente vengono create delle tuple di coppie di stringhe che corrispondono a quelle con cui dovrebbero esser create le sotto-sotto-chiavi delle coppie di condizioni sperimentali..

tuttavia, è giusto che iteri rispetto a 'condition_pairs', ma deve inserire un qualche controllo anche rispetto a questa cosa:

originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo

print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n") print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n") print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n") print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")

Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza, nel tuo codice, ho bisogno che

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, che nel caso di "condition_pairs" dovrebbe corrispondere ai primi 3 elementi della sua lista no, perché sarebbero 

[('baseline', 'th_resp'), 
    ('baseline', 'pt_resp'), 
    ('baseline', 'shared_resp'), 

è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare, che fa riferimento a questi altri elementi di 
"condition_pairs" che è creato nel loop ossia

('th_resp', 'pt_resp'), 
('th_resp', 'shared_resp'), 
('pt_resp', 'shared_resp')]

le labels andranno ovviamente riconvertite! Perché? 

Perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempio, in quel caso, le sue labels (che son originariamente codificate come '1' in 'new_subject_level_concatenations'!) diventeranno '0',

mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...

è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?dentro "# Crea tutte le combinazioni uniche di condizioni sperimentali (es. 'baseline vs th_resp')
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
    "

effettivamente vengono create delle tuple di coppie di stringhe che corrispondono a quelle con cui dovrebbero esser create le sotto-sotto-chiavi delle coppie di condizioni sperimentali..

tuttavia, è giusto che iteri rispetto a 'condition_pairs', ma deve inserire un qualche controllo anche rispetto a questa cosa:

originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo

print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n") print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n") print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n") print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")

Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza, nel tuo codice, ho bisogno che

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, che nel caso di "condition_pairs" dovrebbe corrispondere ai primi 3 elementi della sua lista no, perché sarebbero 

[('baseline', 'th_resp'), 
    ('baseline', 'pt_resp'), 
    ('baseline', 'shared_resp'), 

è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare, che fa riferimento a questi altri elementi di 
"condition_pairs" che è creato nel loop ossia

('th_resp', 'pt_resp'), 
('th_resp', 'shared_resp'), 
('pt_resp', 'shared_resp')]

le labels andranno ovviamente riconvertite! Perché? 

Perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempio, in quel caso, le sue labels (che son originariamente codificate come '1' in 'new_subject_level_concatenations'!) diventeranno '0',

mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...

è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?



##### Implementazione STEP - Concatenazione All Single Subject Spectrograms (TH) across Couples of Experimental Conditions

In [115]:
new_single_pt_all_extracted_spectrograms_2D.keys()

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [116]:
new_single_pt_all_extracted_spectrograms_2D['spectrograms_baseline_1'].keys()

dict_keys(['spectrograms', 'labels'])

In [117]:
type(new_single_pt_all_extracted_spectrograms_2D['spectrograms_baseline_1'])

dict

In [118]:
print(f"Baseline in TH_1:, {np.unique(new_single_pt_all_extracted_spectrograms_2D['spectrograms_baseline_1']['labels'], return_counts = True)}\n")
print(f"Th_Resp in TH_1:, {np.unique(new_single_pt_all_extracted_spectrograms_2D['spectrograms_th_resp_1']['labels'], return_counts = True)}\n")
print(f"Pt_Resp in TH_1:, {np.unique(new_single_pt_all_extracted_spectrograms_2D['spectrograms_pt_resp_1']['labels'], return_counts = True)}\n")
print(f"Shared_Resp in TH_1:, {np.unique(new_single_pt_all_extracted_spectrograms_2D['spectrograms_shared_resp_1']['labels'], return_counts = True)}\n")

Baseline in TH_1:, (array(['0'], dtype='<U1'), array([44]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([43]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([47]))



In [119]:
new_single_pt_all_extracted_spectrograms_2D['spectrograms_baseline_1'].keys()

dict_keys(['spectrograms', 'labels'])

In [120]:
'''DETAILED VERSION WITH COMPLICATED PRINTS

    CORREZIONE UFFICIALE PER SPETTROGRAMS
'''


import itertools
import numpy as np

# Definizione delle condizioni sperimentali
experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']

# Variabile per tenere traccia del soggetto corrente (per output facoltativo)
last_subject_key = None

# Dizionario per tenere traccia delle combinazioni già elaborate per ogni soggetto (evitare duplicati)
printed_combinations = {}

# Nuovo dizionario per memorizzare i risultati concatenati per coppia di condizioni per ogni soggetto
new_subject_level_concatenations_spectrograms_coupled_exp_pt = {}

# Itera su tutte le chiavi del dizionario di partenza
for key in new_single_pt_all_extracted_spectrograms_2D.keys():
    # Esempio di key: "spectrograms_baseline_1", "spectrograms_th_resp_1", etc.
    key_parts = key.split('_')
    subject_number = key_parts[-1] if key_parts[-1].isdigit() else None
    if subject_number is None:
        continue  # Salta eventuali chiavi non valide
    
    # Crea il nome del soggetto (es. "th_1")
    subject_key = f"pt_{subject_number}"
    
    # Se cambiamo soggetto, stampiamo (facoltativo)
    if subject_key != last_subject_key:
        if last_subject_key is not None:
            print("\n" + "-" * 50 + f" END OF {last_subject_key.upper()} " + "-" * 50 + "\n")
        print(f"\nProcessing Subject: {subject_key}\n" + "=" * 80)
        printed_combinations[subject_key] = set()  # Inizializza il set per il soggetto corrente
    last_subject_key = subject_key

    # Inizializza la struttura per il soggetto se non esiste già
    if subject_key not in new_subject_level_concatenations_spectrograms_coupled_exp_pt:
        new_subject_level_concatenations_spectrograms_coupled_exp_pt[subject_key] = {}

    # Crea tutte le combinazioni uniche di condizioni sperimentali (es. "baseline_vs_th_resp")
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
    
    # Loop sulle coppie di condizioni
    for cond_1, cond_2 in condition_pairs:
        condition_pair_key = f"{cond_1}_vs_{cond_2}"
        if condition_pair_key in printed_combinations[subject_key]:
            continue  # Salta se già elaborata per questo soggetto
        
        print(f"\n\tCreation of Coupled Condition: \033[1m{condition_pair_key}\033[0m")
        printed_combinations[subject_key].add(condition_pair_key)
        
        # Estrai i dati e le etichette per la prima condizione
        data_cond_1 = new_single_pt_all_extracted_spectrograms_2D.get(f"spectrograms_{cond_1}_{subject_number}", {}).get('spectrograms')
        labels_cond_1 = new_single_pt_all_extracted_spectrograms_2D.get(f"spectrograms_{cond_1}_{subject_number}", {}).get('labels')
        
        # Estrai i dati e le etichette per la seconda condizione
        data_cond_2 = new_single_pt_all_extracted_spectrograms_2D.get(f"spectrograms_{cond_2}_{subject_number}", {}).get('spectrograms')
        labels_cond_2 = new_single_pt_all_extracted_spectrograms_2D.get(f"spectrograms_{cond_2}_{subject_number}", {}).get('labels')
        
        # Salta la coppia se uno dei dati non è presente
        if data_cond_1 is None or labels_cond_1 is None or data_cond_2 is None or labels_cond_2 is None:
            continue
        
        # Riassegna le etichette: tutti 0 per cond_1, tutti 1 per cond_2
        labels_cond_1 = np.zeros_like(labels_cond_1, dtype=int)
        labels_cond_2 = np.ones_like(labels_cond_2, dtype=int)
        
        # Concatenazione dei dati (verticale) e delle etichette (orizzontale)
        concatenated_data = np.concatenate((data_cond_1, data_cond_2), axis=0)
        concatenated_labels = np.concatenate((labels_cond_1, labels_cond_2), axis=0)
        
        # Salva il risultato per questa coppia nel dizionario del soggetto
        new_subject_level_concatenations_spectrograms_coupled_exp_pt[subject_key][condition_pair_key] = {
            'data': concatenated_data,
            'labels': concatenated_labels
        }
        
        print(f"Condition pair '{condition_pair_key}' for subject {subject_key} => Data shape: {concatenated_data.shape}, Labels length: {len(concatenated_labels)}")



Processing Subject: pt_1

	Creation of Coupled Condition: baseline_vs_th_resp
Condition pair 'baseline_vs_th_resp' for subject pt_1 => Data shape: (84, 45, 61), Labels length: 84

	Creation of Coupled Condition: baseline_vs_pt_resp
Condition pair 'baseline_vs_pt_resp' for subject pt_1 => Data shape: (87, 45, 61), Labels length: 87

	Creation of Coupled Condition: baseline_vs_shared_resp
Condition pair 'baseline_vs_shared_resp' for subject pt_1 => Data shape: (91, 45, 61), Labels length: 91

	Creation of Coupled Condition: th_resp_vs_pt_resp
Condition pair 'th_resp_vs_pt_resp' for subject pt_1 => Data shape: (83, 45, 61), Labels length: 83

	Creation of Coupled Condition: th_resp_vs_shared_resp
Condition pair 'th_resp_vs_shared_resp' for subject pt_1 => Data shape: (87, 45, 61), Labels length: 87

	Creation of Coupled Condition: pt_resp_vs_shared_resp
Condition pair 'pt_resp_vs_shared_resp' for subject pt_1 => Data shape: (90, 45, 61), Labels length: 90

-------------------------------

In [121]:
print(f"\t\t\t\t\033[1mStructure of new_subject_level_concatenations_spectrograms_coupled_exp_th\033[0m: \n")
print(f"\033[1mFirst Order Keys\033[0m: {new_subject_level_concatenations_spectrograms_coupled_exp_pt.keys()}\n")
print(f"\033[1mSecond Order Keys\033[0m: {new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1'].keys()}\n")
print(f"\033[1mThird Order Keys\033[0m: \n{new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1']['baseline_vs_th_resp'].keys()}\n")

				Structure of new_subject_level_concatenations_spectrograms_coupled_exp_th: 

First Order Keys: dict_keys(['pt_1', 'pt_2', 'pt_3', 'pt_4', 'pt_5', 'pt_6', 'pt_7', 'pt_8', 'pt_9', 'pt_10', 'pt_11', 'pt_12', 'pt_13', 'pt_14', 'pt_15', 'pt_16', 'pt_17', 'pt_18', 'pt_19', 'pt_20'])

Second Order Keys: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

Third Order Keys: 
dict_keys(['data', 'labels'])



In [122]:
'''VERIFICO CHE LA CONCATENAZIONE SIA AVVENUTA CORRETTAMENTE!

    CORREZIONE UFFICIALE PER SPETTROGRAMS
'''

print("\tNOW, LET US SEE IF THE CONCATENATIONS RESPECT THE ORIGINAL SHAPES FOR EVERY COUPLED EXPERIMENTAL CONDITION!")
print("\tFOR THE 1°ST SUBJECT: CHECK IF THE SUM OF INDIVIDUAL EXP COND SHAPE MATCHES THE COUPLED COND CONCATENATION SHAPE:\n\n")

print("\033[1mINDIVIDUAL EXP COND SHAPE OF FIRST SUBJECT\033[0m:")

# Verifica delle dimensioni originali per le singole condizioni sperimentali
for cond in ['baseline', 'th_resp', 'pt_resp', 'shared_resp']:
    key = f'spectrograms_{cond}_1'
    if key in new_single_pt_all_extracted_spectrograms_2D:
        unique_labels, counts = np.unique(new_single_pt_all_extracted_spectrograms_2D[key]['labels'], return_counts=True)
        print(f"{cond.capitalize()} in TH_1: {unique_labels}, Counts: {counts}\n")
    else:
        print(f"Warning: {key} not found in new_single_pt_all_extracted_spectrograms_2D\n")

# Seleziona il primo soggetto (ad esempio, 'th_1')
subject_key = 'pt_1'

# Itera per ogni coppia di condizioni sperimentali direttamente (senza livelli)
for condition_pair_key, data_labels in new_subject_level_concatenations_spectrograms_coupled_exp_pt.get(subject_key, {}).items():
    
    # Estrarre dati e labels dalla struttura corretta
    data = data_labels['data']
    labels = data_labels['labels']

    # Stampare il nome della coppia di condizioni e le loro dimensioni
    print(f"Condition Pair: \033[1m{condition_pair_key}\033[0m")
    
    if data is not None and labels is not None:
        print(f"  Data Shape: {data.shape}")
        print(f"  Labels Shape: {labels.shape}")
    else:
        print("  Missing data or labels!")

        

	NOW, LET US SEE IF THE CONCATENATIONS RESPECT THE ORIGINAL SHAPES FOR EVERY COUPLED EXPERIMENTAL CONDITION!
	FOR THE 1°ST SUBJECT: CHECK IF THE SUM OF INDIVIDUAL EXP COND SHAPE MATCHES THE COUPLED COND CONCATENATION SHAPE:


INDIVIDUAL EXP COND SHAPE OF FIRST SUBJECT:
Baseline in TH_1: ['0'], Counts: [44]

Th_resp in TH_1: ['1'], Counts: [40]

Pt_resp in TH_1: ['2'], Counts: [43]

Shared_resp in TH_1: ['3'], Counts: [47]

Condition Pair: baseline_vs_th_resp
  Data Shape: (84, 45, 61)
  Labels Shape: (84,)
Condition Pair: baseline_vs_pt_resp
  Data Shape: (87, 45, 61)
  Labels Shape: (87,)
Condition Pair: baseline_vs_shared_resp
  Data Shape: (91, 45, 61)
  Labels Shape: (91,)
Condition Pair: th_resp_vs_pt_resp
  Data Shape: (83, 45, 61)
  Labels Shape: (83,)
Condition Pair: th_resp_vs_shared_resp
  Data Shape: (87, 45, 61)
  Labels Shape: (87,)
Condition Pair: pt_resp_vs_shared_resp
  Data Shape: (90, 45, 61)
  Labels Shape: (90,)


In [123]:
print(np.unique(new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1']['baseline_vs_th_resp']['labels'], return_counts = True))
print(np.unique(new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1']['th_resp_vs_shared_resp']['labels'], return_counts = True))

(array([0, 1]), array([44, 40]))
(array([0, 1]), array([40, 47]))


In [124]:
print(f"\t\t\t\033[1mBASELINE_VS_TH_RESP\033[0m\n")
print(new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1']['baseline_vs_th_resp']['labels'][:51])
print(new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1']['baseline_vs_th_resp']['labels'][51:])
print()
print()
print(f"\t\t\t\033[1mTH_RESP_VS_SHARED_RESP\033[0m\n")
print(new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1']['th_resp_vs_shared_resp']['labels'][:40])
print(new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1']['th_resp_vs_shared_resp']['labels'][40:])


			BASELINE_VS_TH_RESP

[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 1 1 1 1 1 1 1]
[1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]


			TH_RESP_VS_SHARED_RESP

[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0]
[1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
 1 1 1 1 1 1 1 1 1 1]


##### STEP - Salvataggio Dataset di All Single Therapists EEG Data Spectrograms across Couples of Experimental Conditions

In [125]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [126]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''
import pickle

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_subject_level_concatenations_spectrograms_coupled_exp_pt.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_spectrograms_coupled_exp_pt, f)

#### **Concatenazione** **ALL** Single Subject **Spectrograms (PT)** per **Coppie di Condizioni Sperimentali INSIEME**

In [127]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_NF '''

import pickle
import numpy as np

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_subject_level_concatenations_spectrograms_coupled_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_spectrograms_coupled_exp_pt = pickle.load(f)

In [ ]:
#new_subject_level_concatenations_spectrograms_coupled_exp_pt.keys()
#new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1'].keys()
#new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1']['baseline_vs_th_resp'].keys()
#np.unique(new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1']['baseline_vs_th_resp']['labels'], return_counts = True)

In [128]:
np.unique(new_subject_level_concatenations_spectrograms_coupled_exp_pt['pt_1']['baseline_vs_th_resp']['labels'], return_counts = True)

(array([0, 1]), array([44, 40]))

In [129]:
'''CODICE UFFICIALE CON MODIFICHE A SPETTROGRAMMI'''


import numpy as np

def concatenate_all_subjects_coupled_spectrogram_conditions_pt(data_structure, conditions):
    
    """
    Concatena globalmente i dati e le etichette per ogni coppia di condizioni sperimentali
    a partire dalla struttura 'new_subject_level_concatenations_spectrograms_coupled_exp_th'.
    I dati di ogni soggetto (già raggruppati per coppia di condizioni) vengono ulteriormente 
    concatenati per ottenere un unico array globale per ogni coppia.
    
    Parameters:
        data_structure (dict): Struttura dati con chiavi per soggetto (es. 'pt_1', 'pt_2', ...)
                               e, per ciascun soggetto, chiavi per ciascuna coppia di condizioni sperimentali.
        condition_pairs (list): Lista di coppie di condizioni sperimentali (es. 'baseline_vs_th_resp', ...)
        
    Returns:
        dict: Un dizionario globale in cui ogni chiave è una coppia di condizioni e il valore
              è un dizionario con 'data' e 'labels' concatenati globalmente (da tutti i soggetti).
    """
        
    # Dizionario per contenere i dati concatenati di tutti i soggetti
    all_subj_data_by_coupled_cond = {}

    # Itera su ogni coppia di condizioni sperimentali
    for condition_pair in conditions:

        #Dizionari per raccogliere dati e labels ordinati per ogni coppia di condizioni sperimentali
        # che è dinamico, per ogni coppia di condizioni sperimentali 
        #(quindi si ricreeranno passando alla condizione sperimentale successiva!)

        data_by_label = {}
        labels_by_label = {}
        shape_labels_per_subject = {0: [], 1: []}  # Inizializza il dizionario per 0 e 1

        # Itera su tutti i soggetti
        # In questo caso, itera sulle chiavi di ogni soggetto

        # Quindi prenderà, per la relativa coppia di condizioni sperimentali di ogni soggetto,
        # i dati e le labels di quel soggetto, per quella relativa coppia di condizioni sperimentali

        for subject_key in data_structure.keys():

            # Controlla se il livello di ricostruzione esiste per il soggetto
            if condition_pair not in data_structure[subject_key]:
                continue

            # Qui estrae i dati e le labels per questa condizione sperimentale di quel soggettio lì
            subject_data = data_structure[subject_key][condition_pair]['data']
            subject_labels = data_structure[subject_key][condition_pair]['labels']

            # Trova le etichette uniche e gli indici corrispondenti per quella coppia di condizioni sperimentali lì,
            # Ossia, potrà trovare gli 0 e gli 1 

            unique_labels = np.unique(subject_labels)

            #A quel punto, per ognuna delle due labels trovate per quella coppia di condizioni sperimentali lì
            #Che saranno sempre o 0 o 1

            for label in unique_labels:

                # Trova gli indici dei dati corrispondenti a questa etichetta
                # Una volta per lo 0 ed una volta per l' 1

                label_indices = np.where(subject_labels == label)[0]

                # A quel punto, estrae i dati e le labels per questi indici
                # Una volta per lo 0 ed una volta per l' 1

                data_for_label = subject_data[label_indices]
                labels_for_label = subject_labels[label_indices]

                # A quel punto, per ogni soggetto, per ogni condzione sperimentale, 
                # per quelle due labels là (sempre presenti, per ogni coppia di condizioni sperimentali)
                # Una volta per lo 0 ed una volta per l' 1

                #Andrà a creare per ogni etichetta, una chiave che si chiamerà 
                #o 0 od 1 (inizialmente, vuoto -> perché deve esser inizializzato)
                #E poi, dopo, ci appenderà le labels 
                 # Una volta per lo 0 ed una volta per l' 1
                #  Di quel soggetto per quella coppia di condizioni sperimentali iterate a quel momento

                #Aggiunge ai dizionari globali, creando la chiave se non esiste
                if label not in data_by_label:
                    data_by_label[label] = []
                    labels_by_label[label] = []

                data_by_label[label].append(data_for_label)
                labels_by_label[label].append(labels_for_label)

                # **Salva la shape delle etichette per il soggetto corrente**
                shape_labels_per_subject[label].append(labels_for_label.shape[0]) # Aggiungi solo la dimensione (numero di etichette)

                '''PRINT PER CHECK LABELS DI OGNI SOGGETTO PER OGNI COPPIA DI CONDIZIONE CONDIZIONI SPERIMENTALI''' 
                #print(f"Soggetto: \033[1m{subject_key}\033[0m, Livello: \033[1m{reconstruction_level}\033[0m, Condizione: \033[1m{condition_pair}\033[0m, "
                #      f"Etichetta: \033[1m{label}\033[0m, Shape: \033[1m{labels_for_label.shape[0]}\033[0m")

                # **Aggiungi un print di controllo per ogni soggetto**
                #print(f"Soggetto: \033[1m{subject_key}\033[1m, Livello: {reconstruction_level}, Condizione: {condition_pair}, Etichetta: {label}, Shape: {labels_for_label.shape[0]}")

            
        #*** *** *** *** *** *** *** *** *** *** *** *** *** *** ***

        # Dopodiché, vado a creare invece i dizionari che conterranno
        # Le concatenazioni, di dati e labels corrispondenti, di tutti i soggetti per cui l'etichetta era 
        # o 0 od 1 

        # Di conseguenza, qui dentro dovrei avere, per ogni coppia di condizioni sperimentali
        # Tutti gli 0 ed 1 (ed i relativi dati corrispondenti)
        # di tutti i soggetti, ma concatenati

        concatenated_data_by_label = {}
        concatenated_labels_by_label = {}

        #for label in data_by_label.keys():
        #    if len(data_by_label[label]) > 0:  # Evita errori di concatenazione
        #        concatenated_data_by_label[label] = np.vstack(data_by_label[label])
        #        concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
            
        for label in data_by_label.keys():
            concatenated_data_by_label[label] = np.vstack(data_by_label[label])
            concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])

            # **Calcolare la shape totale delle etichette**
            #total_labels_0 = np.sum(1 for subject_labels in labels_by_label[label] if 0 in subject_labels)
            #total_labels_1 = np.sum(1 for subject_labels in labels_by_label[label] if 1 in subject_labels)
            #total_labels = total_labels_0 + total_labels_1

            # **Determinare gli indici delle etichette 0 e 1 nell'array finale**

            # Gli indici delle etichette 0
            indices_labels_0 = np.where(concatenated_labels_by_label[label] == 0)[0]

            # Gli indici delle etichette 1
            indices_labels_1 = np.where(concatenated_labels_by_label[label] == 1)[0]

            # Indici iniziale e finale per le etichette 0 e 1
            start_idx_0 = indices_labels_0[0] if len(indices_labels_0) > 0 else None
            end_idx_0 = indices_labels_0[-1] if len(indices_labels_0) > 0 else None
            start_idx_1 = indices_labels_1[0] if len(indices_labels_1) > 0 else None
            end_idx_1 = indices_labels_1[-1] if len(indices_labels_1) > 0 else None


            # **Print finale per verificare la concatenazione per ogni label**
            #print(f"\nCondizione: \033[1m{condition_pair}\033[0m, Etichetta: {label}")
            #print(f"  - Shape dei dati concatenati per \033[1m{label}\033[0m: {concatenated_data_by_label[label].shape}")
            #print(f"  - Shape delle etichette concatenate per \033[1m{label}\033[0m: {concatenated_labels_by_label[label].shape}")

            # **Stampa la lista delle shapes delle etichette per ogni soggetto per questa etichetta**
            #print(f"\n  - Shape delle etichette per soggetto (per etichetta {label}): {shape_labels_per_subject[label]}\n")


            # **Stampa il conteggio totale delle etichette**
            #print(f"\n  - Totale delle etichette 0: {total_labels_0}")
            #print(f"  - Totale delle etichette 1: {total_labels_1}")
            #print(f"  - Totale delle etichette per la condizione: {total_labels}\n")

            # **Stampa gli indici per le etichette 0 e 1**
            # **OSSIA --> Stampa gli indici per l'etichetta corrente**

            #if label == 0:
            #    print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #else:
            #    print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}\n")


            #print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}")


        #ARRIVATI FINO A QUI, abbiamo che siccome stiamo iterando prima per tutti gli 0 e poi per tutti gli 1
        #Significa che, assumendo che siamo dentro 'baseline_vs_th_resp' e che 

        #'baseline' sia rappresentato dalle etichette 0
        #'th_resp' sia rappresentato dalle etichette 1

        #Al PRIMO ciclo avrò che:

        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'baseline' per 'baseline_vs_th_resp'di tutti i soggetti)

        #Al SECONDO ciclo avrò che:

        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)

        #Quindi mi manca ancora 

        #A) CONCATENARE I DATI:

        #1)prima tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 

        #CON

        #2)tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)

        #che verrà fatto dentro all_data (che è anch'esso una variabile dinamica!)

        #B) CONCATENARE LE LABELS:

        #1)prima tutti le labels (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 

        #CON

        #2)tutti le labels (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)

        #che verrà fatto dentro all_labels (che è anch'esso una variabile dinamica!)

        # Liste per raccogliere dati e labels di tutte le etichette

        # Qui dentro, invece, dov con

        all_data = []
        all_labels = []

        for label in concatenated_data_by_label.keys():
            all_data.append(concatenated_data_by_label[label])
            all_labels.append(concatenated_labels_by_label[label])

        #Alla fine, qui dentro avrò che, PER OGNI COPPIA DI CONDIZIONI SPERIMENTALI


        #'final_data' dovrebbe avere 
            #- prima tutti i dati di tutti i soggetti associati all'etichetta 0 
            #- e poi tutti i dati di tutti i soggetti associati all'etichetta 1

        #'final_labels' dovrebbe avere 
            #- prima tutte le labels di tutti i soggetti associati all'etichetta 0
            #- e poi tutte tutte le labels di tutti soggetti associati all'etichetta 1...

        if all_data:  # Evita errori di concatenazione se non ci sono dati
            final_data = np.vstack(all_data)
            final_labels = np.hstack(all_labels)

            all_subj_data_by_coupled_cond[condition_pair] = {
                'data': final_data,
                'labels': final_labels
            }
            
    return all_subj_data_by_coupled_cond


In [130]:
# Parametri
conditions = ['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp',
              'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp']

# Chiamata alla funzione, qui definisco a mano il nome della variabile (i.e., 
new_all_pt_concat_spectrograms_coupled_exp = concatenate_all_subjects_coupled_spectrogram_conditions_pt(
    data_structure=new_subject_level_concatenations_spectrograms_coupled_exp_pt,
    conditions=conditions
)

print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")


for condition_pair, value in new_all_pt_concat_spectrograms_coupled_exp.items():
    labels = value['labels']
    unique_labels = np.unique(labels)
    total_labels = 0

    print(f"\nCondizione: \033[1m{condition_pair}\033[0m")
    for label in unique_labels:
        label_indices = np.where(labels == label)[0]
        start_idx = label_indices[0] if len(label_indices) > 0 else None
        end_idx = label_indices[-1] if len(label_indices) > 0 else None
        total_labels += len(label_indices)

        print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m "
              f"(Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

    print(f"Totale etichette (0 e 1): \033[1m{total_labels}\033[0m\n")


Intervalli di indici per ciascuna etichetta nei sotto-dizionari:


Condizione: baseline_vs_th_resp
  Etichetta 0: Indici 0-1122 (Totale Etichette: 1123)
  Etichetta 1: Indici 1123-1910 (Totale Etichette: 788)
Totale etichette (0 e 1): 1911


Condizione: baseline_vs_pt_resp
  Etichetta 0: Indici 0-1122 (Totale Etichette: 1123)
  Etichetta 1: Indici 1123-1914 (Totale Etichette: 792)
Totale etichette (0 e 1): 1915


Condizione: baseline_vs_shared_resp
  Etichetta 0: Indici 0-1122 (Totale Etichette: 1123)
  Etichetta 1: Indici 1123-2255 (Totale Etichette: 1133)
Totale etichette (0 e 1): 2256


Condizione: th_resp_vs_pt_resp
  Etichetta 0: Indici 0-787 (Totale Etichette: 788)
  Etichetta 1: Indici 788-1579 (Totale Etichette: 792)
Totale etichette (0 e 1): 1580


Condizione: th_resp_vs_shared_resp
  Etichetta 0: Indici 0-787 (Totale Etichette: 788)
  Etichetta 1: Indici 788-1920 (Totale Etichette: 1133)
Totale etichette (0 e 1): 1921


Condizione: pt_resp_vs_shared_resp
  Etichetta 0: Indic

##### STEP - Salvataggio Dataset di **All Single Therapists** EEG Data Spectrograms across **Couples of Experimental Conditions** INSIEME

In [131]:
pwd

'/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45'

In [132]:
cd New_Plots_Sliding_Estimator_MNE_1_45

[Errno 2] No such file or directory: 'New_Plots_Sliding_Estimator_MNE_1_45'
/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [133]:
#cd Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/

In [134]:
'''PATH  --> cd Unfamiliar_Wavelet_Reconstructions'''

import pickle
import os

# Controlla se la cartella esiste, altrimenti la crea
#if not os.path.exists(fam_path):
#    os.makedirs(fam_path)

   
#base_path = '/home/stefano/Interrogait/all_datas/Unfamiliar_Spectrograms'

# Controlla se la cartella esiste, altrimenti la crea
#if not os.path.exists(base_path):
#    os.makedirs(base_path)

# Salvare l'intero dizionario annidato con pickle
#with open(f'{base_path}/new_all_th_concat_spectrograms_coupled_exp.pkl', 'wb') as f:
#    pickle.dump(new_all_th_concat_spectrograms_coupled_exp, f)
    


#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45'
#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_all_pt_concat_spectrograms_coupled_exp.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_spectrograms_coupled_exp, f)

#### **Concatenazione** All **SINGLE** Subject **Spectrograms (PT)** per **Triplets of Experimental Conditions**

##### Procedura

Per calcolare quante possibili triplette (combinazioni di 3 condizioni sperimentali) si possono formare da un insieme di 4 condizioni, utilizziamo il concetto di combinazioni senza ripetizione. La formula per il numero di combinazioni è:

C(n,k)=  k!⋅(n−k)! / n!

Dove:

- n è il numero totale di elementi nell'insieme (n = 4 in questo caso)
- k è il numero di elementi scelti (k = 3)


**Calcoliamo**:

C(4,3)= 4!/ 3⋅(4−3)! = 4⋅3⋅2⋅1 / (3⋅2⋅1)⋅1 = 4 

**Risultato**

Ci sono 4 possibili triplette che si possono formare dalle 4 condizioni sperimentali.

**Elenco delle Triplette**

Se vogliamo enumerarle:

['baseline', 'th_resp', 'pt_resp']
['baseline', 'th_resp', 'shared_resp']
['baseline', 'pt_resp', 'shared_resp']
['th_resp', 'pt_resp', 'shared_resp']

Queste sono tutte le combinazioni possibili


##### Implementazione

In [135]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [136]:
cd ..

/home/stefano/Interrogait


In [137]:
cd New_Plots_Sliding_Estimator_MNE_1_45

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [138]:
import pickle
import numpy as np

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{fam_path}new_single_pt_all_extracted_spectrograms_2D.pkl', 'rb') as f:
    new_single_pt_all_extracted_spectrograms_2D = pickle.load(f)


In [139]:
print(new_single_pt_all_extracted_spectrograms_2D.keys())
print()
print(new_single_pt_all_extracted_spectrograms_2D['spectrograms_baseline_1'].keys())

dict_keys(['spectrograms_baseline_1', 'spectrograms_th_resp_1', 'spectrograms_pt_resp_1', 'spectrograms_shared_resp_1', 'spectrograms_baseline_2', 'spectrograms_th_resp_2', 'spectrograms_pt_resp_2', 'spectrograms_shared_resp_2', 'spectrograms_baseline_3', 'spectrograms_th_resp_3', 'spectrograms_pt_resp_3', 'spectrograms_shared_resp_3', 'spectrograms_baseline_4', 'spectrograms_th_resp_4', 'spectrograms_pt_resp_4', 'spectrograms_shared_resp_4', 'spectrograms_baseline_5', 'spectrograms_th_resp_5', 'spectrograms_pt_resp_5', 'spectrograms_shared_resp_5', 'spectrograms_baseline_6', 'spectrograms_th_resp_6', 'spectrograms_pt_resp_6', 'spectrograms_shared_resp_6', 'spectrograms_baseline_7', 'spectrograms_th_resp_7', 'spectrograms_pt_resp_7', 'spectrograms_shared_resp_7', 'spectrograms_baseline_8', 'spectrograms_th_resp_8', 'spectrograms_pt_resp_8', 'spectrograms_shared_resp_8', 'spectrograms_baseline_9', 'spectrograms_th_resp_9', 'spectrograms_pt_resp_9', 'spectrograms_shared_resp_9', 'spectro

In [140]:
'''NEW IMPLEMENTATION'''

import itertools
import numpy as np

# Definisci le condizioni sperimentali
experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']

# Nuovo dizionario di output per le triplette
new_subject_level_concatenations_spectrograms_triplets_exp_pt = {}

'''

PROBLEMA:

Nel codice che ho fornito,
sto creando delle chiavi per i soggetti come th_1, th_2, etc.,
basate sui numeri estratti dalle chiavi di new_single_pt_all_extracted_spectrograms_2D. 

Tuttavia, l'ordinamento che sto usando potrebbe non essere numericamente corretto... 

Quando si crea una lista di numeri con la funzione sorted(set(...)), 
Python li ordina lessicograficamente come STRINGHE (STR), quindi th_10 verrà messo prima di th_2 
(perché la stringa '10' viene considerata più piccola di '2').


# Estrai i numeri unici dei soggetti dalle chiavi di new_single_pt_all_extracted_spectrograms_2D
#CON ORDINAMENTO LESSICOGRAFICO DI STRINGHE
#unique_subject_numbers = sorted(set(key.split('_')[-1] for key in new_single_pt_all_extracted_spectrograms_2D.keys() 
#                                     if key.split('_')[-1].isdigit()))


SOLUZIONE:

Si può risolvere questo problema modificando il modo in cui ordini i numeri,
trattandoli come NUMERI INTERI (INT), non come stringhe.
A tal fine, puoi usare un approccio simile a quello che ti ho suggerito prima,
ovvero estrarre il numero del soggetto e ordinarlo correttamente come intero. Invece di utilizzare sorted(set(...))
'''

#CON ORDINAMENTO BASATO SUGLI INTEGER

unique_subject_numbers = sorted(
    set(int(key.split('_')[-1]) for key in new_single_pt_all_extracted_spectrograms_2D.keys() if key.split('_')[-1].isdigit())
)

# Itera su ogni soggetto (per esempio, "1", "2", "3", ecc.)
for subject in unique_subject_numbers:
    subject_key = f"pt_{subject}"
    new_subject_level_concatenations_spectrograms_triplets_exp_pt[subject_key] = {}
    
    print(f"\nProcessing Subject: {subject_key}\n" + "=" * 80)
    
    # Crea tutte le combinazioni uniche di triplette di condizioni sperimentali
    condition_triplets = list(itertools.combinations(experimental_conditions, 3))
    
    # Loop su ogni triplette di condizioni
    for cond1, cond2, cond3 in condition_triplets:
        condition_triplet_key = f"{cond1}_vs_{cond2}_vs_{cond3}"
        print(f"\n\tCreation of Triplet Condition: \033[1m{condition_triplet_key}\033[0m")
        
        # Costruisci i nomi delle chiavi per ciascuna condizione per questo soggetto
        key_cond1 = f"spectrograms_{cond1}_{subject}"
        key_cond2 = f"spectrograms_{cond2}_{subject}"
        key_cond3 = f"spectrograms_{cond3}_{subject}"
        
        # Verifica che i dati per tutte le condizioni siano presenti
        if key_cond1 not in new_single_pt_all_extracted_spectrograms_2D or \
           key_cond2 not in new_single_pt_all_extracted_spectrograms_2D or \
           key_cond3 not in new_single_pt_all_extracted_spectrograms_2D:
            print(f"\tMissing data for one of the conditions in triplet {condition_triplet_key} for {subject_key}. Skipping.")
            continue
        
        # Estrai i dati e le etichette per ciascuna condizione
        data_cond1 = new_single_pt_all_extracted_spectrograms_2D[key_cond1]['spectrograms']
        labels_cond1 = new_single_pt_all_extracted_spectrograms_2D[key_cond1]['labels']
        
        data_cond2 = new_single_pt_all_extracted_spectrograms_2D[key_cond2]['spectrograms']
        labels_cond2 = new_single_pt_all_extracted_spectrograms_2D[key_cond2]['labels']
        
        data_cond3 = new_single_pt_all_extracted_spectrograms_2D[key_cond3]['spectrograms']
        labels_cond3 = new_single_pt_all_extracted_spectrograms_2D[key_cond3]['labels']
        
        # Assegna etichette fisse per ciascuna condizione (0, 1, 2)
        labels_cond1 = np.zeros(len(labels_cond1), dtype=int)
        labels_cond2 = np.ones(len(labels_cond2), dtype=int)
        labels_cond3 = np.full(len(labels_cond3), 2, dtype=int)
        
        # Concatenazione dei dati (verticale) e delle etichette (orizzontale)
        concatenated_data = np.vstack((data_cond1, data_cond2, data_cond3))
        concatenated_labels = np.hstack((labels_cond1, labels_cond2, labels_cond3))
        
        # Salva il risultato per questa triplette nel dizionario del soggetto
        new_subject_level_concatenations_spectrograms_triplets_exp_pt[subject_key][condition_triplet_key] = {
            'data': concatenated_data,
            'labels': concatenated_labels
        }
        
        print(f"\n\tExtracted Experimental Conditions: "
              f"\n\t\033[1m{key_cond1}\033[0m shape: \t{data_cond1.shape}, \n\t\033[1m{key_cond2}\033[0m shape: {data_cond2.shape}, \n\t\033[1m{key_cond3}\033[0m shape: {data_cond3.shape}")
        print(f"\n\tConcatenated of Triplet Conditions Data shape: {concatenated_data.shape}, Concatenated labels shape: {concatenated_labels.shape}")


Processing Subject: pt_1

	Creation of Triplet Condition: baseline_vs_th_resp_vs_pt_resp

	Extracted Experimental Conditions: 
	spectrograms_baseline_1 shape: 	(44, 45, 61), 
	spectrograms_th_resp_1 shape: (40, 45, 61), 
	spectrograms_pt_resp_1 shape: (43, 45, 61)

	Concatenated of Triplet Conditions Data shape: (127, 45, 61), Concatenated labels shape: (127,)

	Creation of Triplet Condition: baseline_vs_th_resp_vs_shared_resp

	Extracted Experimental Conditions: 
	spectrograms_baseline_1 shape: 	(44, 45, 61), 
	spectrograms_th_resp_1 shape: (40, 45, 61), 
	spectrograms_shared_resp_1 shape: (47, 45, 61)

	Concatenated of Triplet Conditions Data shape: (131, 45, 61), Concatenated labels shape: (131,)

	Creation of Triplet Condition: baseline_vs_pt_resp_vs_shared_resp

	Extracted Experimental Conditions: 
	spectrograms_baseline_1 shape: 	(44, 45, 61), 
	spectrograms_pt_resp_1 shape: (43, 45, 61), 
	spectrograms_shared_resp_1 shape: (47, 45, 61)

	Concatenated of Triplet Conditions Data 

In [141]:
'''CHECK ORDINAMENTO CORRETTO DATI E LABELS NEW VERSION'''

import numpy as np

# Itera su ogni soggetto nel dizionario delle triplette
print("\n\033[1mIndicizzazione dei dati e delle etichette per ogni sotto-tripletta di condizioni sperimentali:\033[0m\n")

for subject_key, triplets_data in new_subject_level_concatenations_spectrograms_triplets_exp_pt.items():
    print(f"\nSoggetto: \033[1m{subject_key}\033[0m")
    print("=" * 80)

    for triplet_key, triplet_data in triplets_data.items():
        print(f"\nTripletta: \033[1m{triplet_key}\033[0m")
        
        # Estrai i dati e le etichette
        concatenated_data = triplet_data['data']
        concatenated_labels = triplet_data['labels']
        
        # Conta le etichette uniche
        unique_labels = np.unique(concatenated_labels)
        
        # Variabile per il conteggio totale
        total_samples = 0
        
        for label in unique_labels:
            # Trova gli indici corrispondenti a questa etichetta
            label_indices = np.where(concatenated_labels == label)[0]
            
            # Determina l'intervallo di indici
            start_idx = label_indices[0]
            end_idx = label_indices[-1]
            
            # Aggiungi il numero di campioni al totale
            total_samples += len(label_indices)
            
            # Stampa le informazioni sull'etichetta
            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m (Totale: {len(label_indices)})")
        
        # Verifica il totale dei campioni
        print(f"\nTotale campioni per la triplette \033[1m{triplet_key}\033[0m: \033[1m{total_samples}\033[0m")
        print("-" * 80)



Indicizzazione dei dati e delle etichette per ogni sotto-tripletta di condizioni sperimentali:


Soggetto: pt_1

Tripletta: baseline_vs_th_resp_vs_pt_resp
  Etichetta 0: Indici 0-43 (Totale: 44)
  Etichetta 1: Indici 44-83 (Totale: 40)
  Etichetta 2: Indici 84-126 (Totale: 43)

Totale campioni per la triplette baseline_vs_th_resp_vs_pt_resp: 127
--------------------------------------------------------------------------------

Tripletta: baseline_vs_th_resp_vs_shared_resp
  Etichetta 0: Indici 0-43 (Totale: 44)
  Etichetta 1: Indici 44-83 (Totale: 40)
  Etichetta 2: Indici 84-130 (Totale: 47)

Totale campioni per la triplette baseline_vs_th_resp_vs_shared_resp: 131
--------------------------------------------------------------------------------

Tripletta: baseline_vs_pt_resp_vs_shared_resp
  Etichetta 0: Indici 0-43 (Totale: 44)
  Etichetta 1: Indici 44-86 (Totale: 43)
  Etichetta 2: Indici 87-133 (Totale: 47)

Totale campioni per la triplette baseline_vs_pt_resp_vs_shared_resp: 134
-

In [142]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [143]:
'''PER SALVARE STRUTTURA DATI E LABEL OGNI SOGGETTO NON ANCORA CONCATENATI TRA DI LORO

PS: viene comunque già salvato in  --> new_subject_level_concatenations_triplets_exp_pt_1_45 '''

import pickle

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Salva il dizionario th_data_dict in un file pkl
with open(f'{fam_path}/new_subject_level_concatenations_spectrograms_triplets_exp_pt.pkl', 'wb') as file:
    pickle.dump(new_subject_level_concatenations_spectrograms_triplets_exp_pt, file)

#### **Concatenazione All** Single **Subject Spectrograms (PT)** per  **Triplets of Experimental Conditions INSIEME**



In [144]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_subject_level_concatenations_spectrograms_triplets_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_spectrograms_triplets_exp_pt = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_subject_level_concatenations_triplets_exp_pt_1_45.pkl', 'rb') as f:
    new_subject_level_concatenations_triplets_exp_pt_1_45 = pickle.load(f)

In [145]:
new_subject_level_concatenations_spectrograms_triplets_exp_pt['pt_1'].keys()

dict_keys(['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp', 'baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp'])

In [146]:
new_subject_level_concatenations_spectrograms_triplets_exp_pt['pt_1']['baseline_vs_th_resp_vs_pt_resp'].keys()

dict_keys(['data', 'labels'])

In [147]:
# Itera attraverso ogni soggetto nel dizionario
for i, subject_data in new_subject_level_concatenations_spectrograms_triplets_exp_pt.items():
    print(f"Soggetto {i}:")
    print("Chiavi presenti:", list(subject_data.keys()))
    print("-" * 50)

Soggetto pt_1:
Chiavi presenti: ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp', 'baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']
--------------------------------------------------
Soggetto pt_2:
Chiavi presenti: ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp', 'baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']
--------------------------------------------------
Soggetto pt_3:
Chiavi presenti: ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp', 'baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']
--------------------------------------------------
Soggetto pt_4:
Chiavi presenti: ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp', 'baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']
--------------------------------------------------
Soggetto pt_5:
Chiavi presenti: ['baseline_vs_th_resp_vs_pt_resp', 'baseline

In [148]:
#def concatenate_all_single_subj_spectrograms_tripled_experimental_conditions_th(data_structure, conditions, prefix, suffix):

def concatenate_all_single_subj_spectrograms_tripled_experimental_conditions_pt(data_structure, conditions, prefix):
    
    """
    Concatena i dati e le etichette per ogni condizione sperimentale da una struttura dati con un livello in più,
    ordinandoli anche per etichetta.

    Parameters:
        data_structure (dict): La struttura dati di input che contiene i dati per soggetti e condizioni.
        conditions (list): Le condizioni sperimentali (chiavi del secondo livello) da processare.
        prefix (str): Il prefisso del nome dinamico del dizionario.
        #suffix (str): Il suffisso del nome dinamico del dizionario.

    Returns:
        dict: Un dizionario contenente i nuovi dizionari con i dati concatenati e le etichette per ogni condizione.
    """
    
    #Questo conterrà i dati complessivi di tutti i soggetti per ogni coppia di condizioni sperimentali
    all_subj_data_by_coupled_cond = {}

    # Itera su ogni condizione sperimentale
    for condition_triplet in conditions:
        
        # Dizionari per raccogliere dati e labels ordinati per ogni coppia di condizioni sperimentali
        # che è dinamico, per ogni coppia di condizioni sperimentali 
        
        #(quindi si ricreeranno passando alla condizione sperimentale successiva!)
        
        
        #print(f"Creo dizionari di dati e labels per la condizione:")
        #print(f"\n{condition_triplet}")
        data_by_label = {}
        labels_by_label = {}
        
        
        # Lista temporanea per salvare la shape delle etichette per ogni soggetto per ogni etichetta iterata
        
        '''
        Per ogni condizione sperimentale, per ognuna delle 2 labels, 
        la shape delle etichette per ogni soggetto, 

        e me le salvi dentro una lista temporanea, che salva in formato la shape (solo il valore numerico) di ogni soggetto 
        per l'etichette iterata per quella condizione sperimentale là.

        poi, a questo livello dei print 

         # **Print finale per verificare la concatenazione per ogni label**
            print(f"Condizione: {condition_triplet}, Etichetta: {label}")
            print(f"  - Shape dei dati concatenati per {label}: {concatenated_data_by_label[label].shape}")
            print(f"  - Shape delle etichette concatenate per {label}: {concatenated_labels_by_label[label].shape}")

        vorrei che mi stampassi anche questa lista alla fine del print, di modo che possa vedere visivamente subito il numero di labels di ogni soggetto associate a quella labels iterata là così da vedere se il conteggio corrisponde visivamente al totale salvate dentro 

        "concatenated_data_by_label[label]"
        '''
        
        shape_labels_per_subject = {0: [], 1: [], 2: []}  # Inizializza un dizionario per le etichette 0 e 1


        # Itera su tutti i soggetti
        # In questo caso, itera sulle chiavi di ogni soggetto
        
        # Quindi prenderà, per la relativa coppia di condizioni sperimentali di ogni soggetto,
        # i dati e le labels di quel soggetto, per quella relativa coppia di condizioni sperimentali
        
        for subject_key in data_structure.keys():
            
            #print(subject_key)
            #print(data_structure.keys())
            
            # Qui estrae i dati e le labels per questa condizione sperimentale di quel soggettio lì
            subject_data = data_structure[subject_key][condition_triplet]['data']
            subject_labels = data_structure[subject_key][condition_triplet]['labels']

            # Trova le etichette uniche e gli indici corrispondenti per quella coppia di condizioni sperimentali lì,
            # Ossia, potrà trovare gli 0 e gli 1 
            
            unique_labels = np.unique(subject_labels)
        
            #A quel punto, per ognuna delle due labels trovate per quella coppia di condizioni sperimentali lì
            #Che saranno sempre o 0 o 1 
            
            for label in unique_labels:
                
                # Trova gli indici dei dati corrispondenti a questa etichetta
                # Una volta per lo 0 ed una volta per l' 1
                
                label_indices = np.where(subject_labels == label)[0]

                # A quel punto, estrae i dati e le labels per questi indici
                # Una volta per lo 0 ed una volta per l' 1
                
                data_for_label = subject_data[label_indices]
                labels_for_label = subject_labels[label_indices]

                # A quel punto, per ogni soggetto, per ogni condzione sperimentale, 
                # per quelle due labels là (sempre presenti, per ogni coppia di condizioni sperimentali)
                # Una volta per lo 0 ed una volta per l' 1
                
                #Andrà a creare per ogni etichetta, una chiave che si chiamerà 
                #o 0 od 1 (inizialmente, vuoto -> perché deve esser inizializzato)
                #E poi, dopo, ci appenderà le labels 
                 # Una volta per lo 0 ed una volta per l' 1
                #  Di quel soggetto per quella coppia di condizioni sperimentali iterate a quel momento
                
                #Aggiunge ai dizionari globali, creando la chiave se non esiste
                if label not in data_by_label:
                    data_by_label[label] = []
                    labels_by_label[label] = []

                data_by_label[label].append(data_for_label)
                labels_by_label[label].append(labels_for_label)
                
                 # **Salva la shape delle etichette per il soggetto corrente**
                shape_labels_per_subject[label].append(labels_for_label.shape[0])  # Aggiungi solo la dimensione (numero di etichette)

        
                # **Aggiungi un print di controllo per ogni soggetto**
                print(f"Soggetto: \033[1m{subject_key}\033[0m, Condizione: \033[1m{condition_triplet}\033[0m, Etichetta: \033[1m{label}\033[0m, Shape: \033[1m{labels_for_label.shape[0]}\033[0m")
                #print(f"  - Numero di \033[1mdati\033[0m per {label}: {data_for_label.shape[0]}")
                #print(f"  - Numero di \033[1metichette\033[0m per {label}: {labels_for_label.shape[0]}")
                
                    
        # Dopodiché, vado a creare invece i dizionari che conterranno
        # Le concatenazioni, di dati e labels corrispondenti, di tutti i soggetti per cui l'etichetta era 
        # o 0 od 1 
        
        # Di conseguenza, qui dentro dovrei avere, per ogni coppia di condizioni sperimentali
        # Tutti gli 0 ed 1 (ed i relativi dati corrispondenti)
        # di tutti i soggetti, ma concatenati
        
        
        concatenated_data_by_label = {}
        concatenated_labels_by_label = {}

        for label in data_by_label.keys():
            concatenated_data_by_label[label] = np.vstack(data_by_label[label])
            concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
            
            # **Calcolare la shape totale delle etichette**
            #total_labels_0 = np.sum(1 for subject_labels in labels_by_label[label] if 0 in subject_labels)
            #total_labels_1 = np.sum(1 for subject_labels in labels_by_label[label] if 1 in subject_labels)
            #total_labels = total_labels_0 + total_labels_1

            # **Determinare gli indici delle etichette 0 e 1 nell'array finale**
            
            # Gli indici delle etichette 0
            indices_labels_0 = np.where(concatenated_labels_by_label[label] == 0)[0]
            
            # Gli indici delle etichette 1
            indices_labels_1 = np.where(concatenated_labels_by_label[label] == 1)[0]
            
            # Gli indici delle etichette 2
            indices_labels_2 = np.where(concatenated_labels_by_label[label] == 2)[0]
            
            # Indici iniziale e finale per le etichette 0 e 1
            start_idx_0 = indices_labels_0[0] if len(indices_labels_0) > 0 else None
            end_idx_0 = indices_labels_0[-1] if len(indices_labels_0) > 0 else None
            
            start_idx_1 = indices_labels_1[0] if len(indices_labels_1) > 0 else None
            end_idx_1 = indices_labels_1[-1] if len(indices_labels_1) > 0 else None
            
            start_idx_2 = indices_labels_2[0] if len(indices_labels_2) > 0 else None
            end_idx_2 = indices_labels_2[-1] if len(indices_labels_2) > 0 else None
    
    
            # **Print finale per verificare la concatenazione per ogni label**
            #print(f"\nCondizione: \033[1m{condition_triplet}\033[0m, Etichetta: {label}")
            #print(f"  - Shape dei dati concatenati per \033[1m{label}\033[0m: {concatenated_data_by_label[label].shape}")
            #print(f"  - Shape delle etichette concatenate per \033[1m{label}\033[0m: {concatenated_labels_by_label[label].shape}")
            
            # **Stampa la lista delle shapes delle etichette per ogni soggetto per questa etichetta**
            #print(f"\n  - Shape delle etichette per soggetto (per etichetta {label}): {shape_labels_per_subject[label]}\n")

            
            # **Stampa il conteggio totale delle etichette**
            #print(f"\n  - Totale delle etichette 0: {total_labels_0}")
            #print(f"  - Totale delle etichette 1: {total_labels_1}")
            #print(f"  - Totale delle etichette per la condizione: {total_labels}\n")

            # **Stampa gli indici per le etichette 0 e 1**
            # **OSSIA --> Stampa gli indici per l'etichetta corrente**
            
            #if label == 0:
            #    print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #else:
            #    print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}\n")

    
            #print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}")

    
        #ARRIVATI FINO A QUI, abbiamo che siccome stiamo iterando prima per tutti gli 0 e poi per tutti gli 1
        #Significa che, assumendo che siamo dentro 'baseline_vs_th_resp' e che 
        
        #'baseline' sia rappresentato dalle etichette 0
        #'th_resp' sia rappresentato dalle etichette 1
        
        #Al PRIMO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'baseline' per 'baseline_vs_th_resp'di tutti i soggetti)
        
        #Al SECONDO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #Quindi mi manca ancora 
        
        #A) CONCATENARE I DATI:
        
        #1)prima tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        
        #che verrà fatto dentro all_data (che è anch'esso una variabile dinamica!)
        
        #B) CONCATENARE LE LABELS:
        
        #1)prima tutti le labels (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti le labels (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #che verrà fatto dentro all_labels (che è anch'esso una variabile dinamica!)
        
        # Liste per raccogliere dati e labels di tutte le etichette
        
        # Qui dentro, invece, dov con
        all_data = []
        all_labels = []

        for label in concatenated_data_by_label.keys():
            all_data.append(concatenated_data_by_label[label])
            all_labels.append(concatenated_labels_by_label[label])
        
        
        #Alla fine, qui dentro avrò che, PER OGNI COPPIA DI CONDIZIONI SPERIMENTALI
        
        
        #'final_data' dovrebbe avere 
            #- prima tutti i dati di tutti i soggetti associati all'etichetta 0 
            #- e poi tutti i dati di tutti i soggetti associati all'etichetta 1
        
        #'final_labels' dovrebbe avere 
            #- prima tutte le labels di tutti i soggetti associati all'etichetta 0
            #- e poi tutte tutte le labels di tutti soggetti associati all'etichetta 1...

        
        # Concatenazione finale per la condizione corrente
        final_data = np.vstack(all_data)
        final_labels = np.hstack(all_labels)
    
        
        # Nome dinamico del dizionario
        #dict_name = f"{prefix}{condition_triplet}{suffix}"
        dict_name = f"{prefix}{condition_triplet}"

        # Salva il risultato nel dizionario globale
        all_subj_data_by_coupled_cond[dict_name] = {
            'data': final_data,
            'labels': final_labels
        }
        
    # Dopo aver costruito tutti i sotto-dizionari, iterare per stampare gli intervalli
    print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")

    for cond_key, cond_data in all_subj_data_by_coupled_cond.items():
        print(f"Condizione: \033[1m{cond_key}\033[0m\n")

        # Estrai le etichette dal sotto-dizionario
        labels = cond_data['labels']

        # Conta le etichette uniche
        unique_labels = np.unique(labels)

        # Variabile per il conteggio totale delle etichette
        total_labels = 0

        # Stampa gli intervalli di indici per ciascuna etichetta
        for label in unique_labels:

            # Trova gli indici corrispondenti a questa etichetta
            label_indices = np.where(labels == label)[0]

            # Determina l'intervallo
            start_idx = label_indices[0]
            end_idx = label_indices[-1]

            # Aggiungi il numero di occorrenze al conteggio totale
            total_labels += len(label_indices)

            # Stampa l'intervallo
            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m (Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

        # Stampa il totale delle etichette per la condizione corrente
        print(f"\nTotale etichette (0, 1 e 2): \033[1m{total_labels}\033[0m\n")

    return all_subj_data_by_coupled_cond

In [149]:
# Parametri

#baseline_vs_th_resp_vs_pt_resp
#baseline_vs_th_resp_vs_shared_resp
#baseline_vs_pt_resp_vs_shared_resp
#th_resp_vs_pt_resp_vs_shared_resp

conditions = ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp','baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']

prefix = "new_all_pt_concat_spectrograms_"
#suffix = "_1_45"

tripled_conditions = list(new_subject_level_concatenations_triplets_exp_pt_1_45['pt_1'].keys())

# Chiamata alla funzione
new_concatenated_dictionaries_pt = concatenate_all_single_subj_spectrograms_tripled_experimental_conditions_pt(
    data_structure=new_subject_level_concatenations_spectrograms_triplets_exp_pt,
    conditions=tripled_conditions,
    prefix=prefix,
    #suffix=suffix
)

# Stampa i risultati per verifica
print('\n\033[1mRISULTATO FINALE TUTTI I SOGGETTI TH\033[0m') 
for key, value in new_concatenated_dictionaries_pt.items():
    print(f"{key}:")
    print(f"  Dati: {value['data'].shape}")
    print(f"  Labels: {value['labels'].shape}")


Soggetto: pt_1, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 0, Shape: 44
Soggetto: pt_1, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 1, Shape: 40
Soggetto: pt_1, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 2, Shape: 43
Soggetto: pt_2, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 0, Shape: 60
Soggetto: pt_2, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 1, Shape: 40
Soggetto: pt_2, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 2, Shape: 43
Soggetto: pt_3, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 0, Shape: 57
Soggetto: pt_3, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 1, Shape: 40
Soggetto: pt_3, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 2, Shape: 40
Soggetto: pt_4, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 0, Shape: 40
Soggetto: pt_4, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 1, Shape: 40
Soggetto: pt_4, Condizione: baseline_vs_th_resp_vs_pt_resp, Etichetta: 2, Sh

##### STEP - Salvataggio Dataset di **All Single Therapists** EEG Data Spectrograms across **Triplets of Experimental Conditions** INSIEME

In [150]:
!pwd

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [151]:
cd ..

/home/stefano/Interrogait


In [152]:
cd New_Plots_Sliding_Estimator_MNE_1_45

/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45


In [153]:
new_concatenated_dictionaries_pt.keys()

dict_keys(['new_all_pt_concat_spectrograms_baseline_vs_th_resp_vs_pt_resp', 'new_all_pt_concat_spectrograms_baseline_vs_th_resp_vs_shared_resp', 'new_all_pt_concat_spectrograms_baseline_vs_pt_resp_vs_shared_resp', 'new_all_pt_concat_spectrograms_th_resp_vs_pt_resp_vs_shared_resp'])

In [154]:
#Mi estraggo ogni sotto-dizionario

new_all_pt_concat_spectrograms_baseline_vs_th_resp_vs_pt_resp = new_concatenated_dictionaries_pt['new_all_pt_concat_spectrograms_baseline_vs_th_resp_vs_pt_resp']

new_all_pt_concat_spectrograms_baseline_vs_th_resp_vs_shared_resp = new_concatenated_dictionaries_pt['new_all_pt_concat_spectrograms_baseline_vs_th_resp_vs_shared_resp']

new_all_pt_concat_spectrograms_baseline_vs_pt_resp_vs_shared_resp = new_concatenated_dictionaries_pt['new_all_pt_concat_spectrograms_baseline_vs_pt_resp_vs_shared_resp']

new_all_pt_concat_spectrograms_th_resp_vs_pt_resp_vs_shared_resp = new_concatenated_dictionaries_pt['new_all_pt_concat_spectrograms_th_resp_vs_pt_resp_vs_shared_resp']


In [155]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_NF '''
import pickle
   
#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms/'

fam_path = '/home/stefano/Interrogait/all_datas/Familiar_Spectrograms_channels_frequencies/'

#'BASELINE VS TH RESP VS PT RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_all_pt_concat_spectrograms_baseline_vs_th_resp_vs_pt_resp.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_spectrograms_baseline_vs_th_resp_vs_pt_resp, f)
                                  
#'BASELINE VS TH RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_all_pt_concat_spectrograms_baseline_vs_th_resp_vs_shared_resp.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_spectrograms_baseline_vs_th_resp_vs_shared_resp, f)
        
#'BASELINE VS PT RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_all_pt_concat_spectrograms_baseline_vs_pt_resp_vs_shared_resp.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_spectrograms_baseline_vs_pt_resp_vs_shared_resp, f)
    
#'TH RESP VS PT RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{fam_path}/new_all_pt_concat_spectrograms_th_resp_vs_pt_resp_vs_shared_resp.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_spectrograms_th_resp_vs_pt_resp_vs_shared_resp, f)

## STEP 4.3.2.2 Wavelet Analysis: Example 12 Therapists

## STEP 4.3.2.2.1 Wavelet Analysis: Ricostruzione Globale da tutti i soggetti

### Variabile "**all_subjects_condition_results**" o "**twelve_th_condition_results**"


**all_subjects_condition_results** contiene un **dizionario per ogni condizione sperimentale di ogni soggetto**, con 
- **chiavi** del tipo 'wave_baseline', 'wave_th_resp', ecc. e con
- un suffisso dinamico numerico (i.e., "_1", "_2") che identifica il soggetto indicizzato. 

Ciascuna di queste chiavi, **mappa su un dizionario** che include:

**'D'**: Coefficienti di dettaglio concatenati per lo stesso soggetto, per ogni trial, canale e livello di decomposizione.

**'A'**: Coefficienti di approssimazione concatenati nello stesso modo di 'D'.

**'Dm'**: Media dei coefficienti di dettaglio sui trial concatenati di ogni canale, della stessa condizione sperimentale per ogni livello.

**'Am'**: Media dei coefficienti di approssimazione sui trial concatenati di ogni canale, della stessa condizione sperimentale per ogni livello.

<br>

**Stato Attuale delle Ricostruzioni**:

Attualmente, ho ottenuto le ricostruzioni del segnale per tutti i trial mediati di ciascun soggetto, per ciascuna condizione sperimentale, canale e livello di decomposizione.
Tuttavia, non ho ancora una media globale delle ricostruzioni tra tutti i soggetti per la stessa condizione sperimentale e per ciascun livello di decomposizione.

### STEP 4.3.2.3.1 Wavelet Analysis -  Next Step: Ottenere la Ricostruzione Media Globale 

L'obiettivo è dunque ottenere una **ricostruzione media globale tra tutti i soggetti**, per una specifica condizione sperimentale e livello di decomposizione! 

Ossia devo calcolare **la media di 'Dm' e 'Am' attraverso TUTTI i soggetti**.

Questa operazione darà una media globale dei coefficienti, che rappresenta la ricostruzione media del segnale per tutti i soggetti, 
rispetto allo stesso canale, della stessa condizione sperimentale, dello stesso livello di ricostruzione. 


### Example: 

"**all_subjects_condition_results['wave_baseline_1']['Am'].shape**"

Output: **(61, 300, 5)**

che sarebbe **la ricostruzione media per ogni canale dei trial di una specifica condizione sperimentale, per ciascun livello di ricostruzione**.

In questo caso, **all_subjects_condition_results['wave_baseline_1']['Am']** rappresenta quindi **la ricostruzione media dei coefficienti di approssimazione per ogni canale, livello di decomposizione, e trial, per la condizione sperimentale 'baseline' per il soggetto 1**.


### STEP 4.3.2.3.1 - Implementazione

### Calcolo della ricostruzione media globale del segnale da ogni canale per la stessa condizione sperimentale fra tutti i soggetti


Per calcolare la ricostruzione media globale tra tutti i soggetti, segui questi passaggi:

- **Filtra i Dati**: Per ogni condizione sperimentale, raccogli i valori di 'Dm' e 'Am' da tutti i soggetti.

- **Concatenazione o Stack**: Usa np.stack per creare array 4D, dove la prima dimensione rappresenta i soggetti, e le altre dimensioni sono (canali, campioni, livelli di decomposizione).

- **Calcola la Media**: Calcola la media lungo la dimensione dei soggetti (asse 0) per ottenere la media globale per ogni canale e livello di decomposizione.


<br>

**Steps**

1) Creo una **lista** (i.e., exp_conditions), che identifichi le **stringhe associate alla stessa condizione sperimentale** per ogni soggetto...

    **exp_conditions** = ['baseline', 'th_resp', 'vision_resp', 'shared_resp']

2) itero sulle chiavi "all_subjects_condition_results", a quel punto filtrare rispetto alla stringa associata alla stessa condizione sperimentale per ogni soggetto dentro exp_conditions, e se è la stessa stringa, tra tutti i soggetti 

(ossia se ad esempio incontra diverse volte delle chiavi con  'baseline', e succederà 15 volte essendo 15 i soggetti)

3) **Prendo la ricostruzione media di Am di tutti i canali di un SINGOLO soggetto** (matrice 3d, con canali, samples e coefficienti del relativo livello)
  
4) La **concateno** con la **stessa ricostruzione media di Am** di tutti i canali di **TUTTI GLI ALTRI soggetti**, ma andando a **creare però una nuova dimensione (generando quindi una matrice 4D)**, che ha come **prima dimensione** i soggetti, e poi seguita dalle altre dimensioni che appartenevano già alla originaria matrice 3D di Am di ogni soggetto (i.e., canali, samples e coefficienti del relativo livello), quindi del tipo:

5) Una volta concatenati questi Am di ogni soggetto tra di loro, rispetto alla stessa condizione sperimentale, **fare la media rispetto alla ricostruzione media di ogni soggetto sulla prima dimensione** (che è quella nuova, ossia dei soggetti)...
   
6) A questo punto **si dovrebbe ri-ottenere una matrice di nuovo 3D**, che avrà canali, n_samples e coeff medi della ricostruzione per ogni livello considerato...
e che **rappresenta per ogni livello di ricostruzione, la ricostruzione media globale dei trial di ogni canale rispetto alla stessa condizione sperimentale di tutti i soggetti**  



In [ ]:
'''TUTTI I SOGGETTI'''

import numpy as np

# Lista delle condizioni sperimentali
exp_conditions = ['baseline', 'th_resp', 'vision_resp', 'shared_resp']

# Dizionario per memorizzare i risultati medi globali per ogni condizione sperimentale
global_mean_results = {}

print(f"\n\033[1mglobal_mean_results\033[0m: ricostruzione medie globali per ciascuna condizione sperimentale, di tutti i soggetti assieme per lo specifico livello di decomposizione")

# Itera su ciascuna condizione sperimentale
for condition in exp_conditions:
    print(f"\nCalcolo della \033[1mmedia globale\033[0m per la condizione sperimentale: \033[1m{condition}\033[0m\n")
    
    # Filtra le chiavi del dizionario che corrispondono alla condizione corrente
    relevant_keys = [key for key in all_subjects_condition_results.keys() if condition in key]

    # Liste per raccogliere tutti i dati Am per la condizione corrente
    Am_list = []

    # Itera sulle chiavi rilevanti e raccogli i dati
    for key in relevant_keys:
        Am_list.append(all_subjects_condition_results[key]['Am'])

    if len(Am_list) == 0:
        print(f"Nessun dato trovato per la condizione '{condition}'.")
        continue

    # Concatenare i dati lungo la dimensione dei soggetti (asse 0)
    Am_concat = np.stack(Am_list, axis=0)  # Stack per creare un array 4D: (soggetti, canali, campioni, livelli)

    # Stampa la forma di Am_concat per conferma
    print(f"\033[1mShape\033[0m di \033[1mAm_concat\033[0m per la condizione '\033[1m{condition}\033[0m': {Am_concat.shape}")

    # Calcola la media globale lungo la dimensione dei soggetti (asse 0)
    global_Am_mean = np.mean(Am_concat, axis=0)

    #Calcola la deviazione standard globale lungo la dimensione dei soggetti (asse 0)
    global_Am_std = np.std(Am_concat, axis=0)

    # Salva i risultati medi globali nel dizionario
    global_mean_results[condition] = {
        
        # Per ogni canale, aggiungo i dati completi dei trial concatenati 
        # di ogni soggetto della stessa condizione sperimentale 
        'all_trials': Am_concat, 

        #Ottengo la media globale per ogni canale
        'global_Am_mean': global_Am_mean,

        #Ottengo la deviazione standard globale per ogni canale
        'global_Am_std': global_Am_std
    }

    # Output delle forme dei dati per conferma

    #global_mean_results ora contiene le medie globali per ciascuna condizione sperimentale, di tutti i soggetti assieme per lo specifico livello di decomposizione
    print(f"\033[1mShape\033[0m di \033[1mglobal_Am_mean\033[0m per la condizione '\033[1m{condition}\033[0m': {global_Am_mean.shape}")
    print(f"\033[1mShape\033[0m di \033[1mglobal_Am_std\033[0m per la condizione '\033[1m{condition}\033[0m': {global_Am_std.shape}")

print(f"\n\n\t\t\tChiavi del dizionario \033[1mglobal_mean_results\033[0m:")
print(f"\t\t\t{global_mean_results.keys()}")

In [ ]:
global_mean_results.keys()

In [ ]:
global_mean_results['baseline']['all_trials'].shape

In [ ]:
#Per ogni canale, ottengo le ricostruzioni ottenute dai coefficienti di approssimazione di ogni livello di decomposizione 
#associato ad ogni trial relativo alla condizione 'baseline' del soggetto 1

print(f"Shape \tall_subjects_condition_results['wave_baseline_1']['A'].shape: {all_subjects_condition_results['wave_baseline_1']['A'].shape}")
print(f"Length \tall_subjects_condition_results['wave_baseline_1']['A_labels']: {len(all_subjects_condition_results['wave_baseline_1']['A_labels'])}")

In [ ]:
'''12  TERAPISTI'''

import numpy as np

# Lista delle condizioni sperimentali
exp_conditions = ['baseline', 'th_resp', 'vision_resp', 'shared_resp']

# Dizionario per memorizzare i risultati medi globali per ogni condizione sperimentale
twelve_global_mean_results = {}

print(f"\n\033[1mtwelve_global_mean_results\033[0m: ricostruzione medie globali per ciascuna condizione sperimentale, di tutti e 12 i soggetti assieme per lo specifico livello di decomposizione")

# Itera su ciascuna condizione sperimentale
for condition in exp_conditions:
    print(f"\nCalcolo della \033[1mmedia globale\033[0m per la condizione sperimentale: \033[1m{condition}\033[0m\n")

    # Filtra le chiavi del dizionario che corrispondono alla condizione corrente
    relevant_keys = [key for key in twelve_th_condition_results.keys() if condition in key]

    # Liste per raccogliere tutti i dati Am per la condizione corrente
    Am_list = []

    # Itera sulle chiavi rilevanti e raccogli i dati
    for key in relevant_keys:
        Am_list.append(twelve_th_condition_results[key]['Am'])

    if len(Am_list) == 0:
        print(f"Nessun dato trovato per la condizione '{condition}'.")
        continue

    # Concatenare i dati lungo la dimensione dei soggetti (asse 0)
    Am_concat = np.stack(Am_list, axis=0)  # Stack per creare un array 4D: (soggetti, canali, campioni, livelli di ricostruzione segnale)

    # Stampa la forma di Am_concat per conferma
    print(f"\033[1mShape\033[0m di \033[1mAm_concat\033[0m per la condizione '\033[1m{condition}\033[0m': {Am_concat.shape}")

    # Calcola la media globale lungo la dimensione dei soggetti (asse 0)
    twelve_global_Am_mean = np.mean(Am_concat, axis=0)

    #Calcola la deviazione standard globale lungo la dimensione dei soggetti (asse 0)
    twelve_global_Am_std = np.std(Am_concat, axis=0)

    # Salva i risultati medi globali nel dizionario
    twelve_global_mean_results[condition] = {
        
        # Per ogni canale, aggiungo i dati completi dei trial concatenati 
        # di ogni soggetto della stessa condizione sperimentale 
        'twelve_th_all_trials': Am_concat, 

        #Ottengo la media globale per ogni canale
        'twelve_global_Am_mean': twelve_global_Am_mean,

        #Ottengo la deviazione standard globale per ogni canale
        'twelve_global_Am_std': twelve_global_Am_std
    }

    # Output delle forme dei dati per conferma

    #global_mean_results ora contiene le medie globali per ciascuna condizione sperimentale, di tutti i soggetti assieme per lo specifico livello di decomposizione
    print(f"\033[1mShape\033[0m di \033[1mtwelve_global_Am_mean\033[0m per la condizione '\033[1m{condition}\033[0m': {twelve_global_Am_mean.shape}")
    print(f"\033[1mShape\033[0m di \033[1mtwelve_global_Am_std\033[0m per la condizione '\033[1m{condition}\033[0m': {twelve_global_Am_std.shape}")

print(f"\n\n\t\t\tChiavi del dizionario \033[1mtwelve_global_mean_results\033[0m:")
print(f"\t\t\t{twelve_global_mean_results.keys()}")


## STEP 4.3.2.3.1 Wavelet Analysis - Plots di All Subjects, All Experimental Conditions (o 12 Therapists)

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

# Indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali: Fz, Cz, Pz

# Nomi dei canali
nomi_canali = ['Fz', 'Cz', 'Pz']

# Livelli di decomposizione desiderati (livelli 3, 4, 5 corrispondenti agli indici 2, 3, 4 in Python)
livelli_di_decomposizione = [2, 3, 4]

# Colori per le condizioni sperimentali
colori_condizioni = {
    'baseline': 'green',
    'th_resp': 'blue',
    'vision_resp': 'purple',
    'shared_resp': 'red'
}

# Frequenza di campionamento
frequenza_campionamento = 250  # Hz
campioni_totali = 300  # Numero di campioni
durata_finestra = 1.2  # Secondi
pre_stimolo_ms = 200  # Millisecondi

# Creazione della figura con una griglia 3x3 (3 canali x 3 livelli di decomposizione)
fig, axs = plt.subplots(3, 3, figsize=(20, 25), sharex=True, sharey=True)  # Aumenta la larghezza a 20

'''ALL THERAPISTS MEAN'''
#fig.suptitle('\n\nRicostruzione del Segnale mediato dai Coefficienti di Approssimazione per ogni Condizione Sperimentale e Livello di Decomposizione di interesse - Media Terapisti', fontsize=16)

'''ALL THERAPISTS MEAN & STD'''
fig.suptitle('\n\nRicostruzione del Segnale mediato dai Coefficienti di Approssimazione per ogni Condizione Sperimentale e Livello di Decomposizione di interesse - Media & Std Terapisti', fontsize=16)

'''12 THERAPISTS MEAN'''
#fig.suptitle('\n\nRicostruzione del Segnale mediato dai Coefficienti di Approssimazione per ogni Condizione Sperimentale e Livello di Decomposizione di interesse - Media 12 Terapisti', fontsize=16)

# Creazione dell'asse x in millisecondi
asse_x_ms = np.linspace(-pre_stimolo_ms, durata_finestra * 1000 - pre_stimolo_ms, campioni_totali)

'''12 THERAPISTS'''
#for idx, (condizione, risultati) in enumerate(twelve_global_mean_results.items()):

'''ALL THERAPISTS'''
# Itera su ogni condizione sperimentale e livello di decomposizione
for idx, (condizione, risultati) in enumerate(global_mean_results.items()):
    
    # Determina il colore basato sulla condizione sperimentale
    colore = colori_condizioni.get(condizione, 'black')  # Colore di default se la condizione non è nella mappa

    '''ALL THERAPISTS'''
    # Forma di risultati['global_Am_mean']
    print(f"\nShape di \033[1mrisultati['global_Am_mean']\033[0m considerando tutti i canali: {risultati['global_Am_mean'].shape}")  

    '''12 THERAPISTS'''
    # Forma di risultati['twelve_global_Am_mean']
    #print(f"\nShape di \033[1mrisultati['twelve_global_Am_mean']\033[0m considerando tutti i canali: {risultati['twelve_global_Am_mean'].shape}")  

    # Itera sul livello i-esimo di decomposizione
    for i, livello in enumerate(livelli_di_decomposizione):

        
        '''ALL THERAPISTS'''
        # Sapendo che 'risultati['global_Am_mean']' abbia dimensioni: (num_canali, num_samples, num_livelli)
        Am_livello = risultati['global_Am_mean'][canali_di_interesse, :, livello]

        '''Aggiunta deviazione standard ALL THERAPISTS: PER PLOT CON STD'''
        std_livello = risultati['global_Am_std'][canali_di_interesse, :, livello]  # Deviazione standard error bar
        
        '''12 THERAPISTS MEAN'''
        # Sapendo che 'risultati['global_Am_mean']' abbia dimensioni: (num_canali, num_samples, num_livelli)
        #twelve_Am_livello = risultati['twelve_global_Am_mean'][canali_di_interesse, :, livello]

        '''12 THERAPISTS STD'''
        #twelve_std_livello = risultati['twelve_global_Am_std'][canali_di_interesse, :, livello]  # Deviazione standard error bar
        
        # Debugging dettagliato
        print(f"\nCondizione: \033[1m{condizione}\033[0m, Livello: \033[1m{livello + 1}\033[0m, Indice livello: \033[1m{livello}\033[0m")
        print(f"\nForma Am per il livello {livello + 1}: {Am_livello.shape}")  # Debugging
        
        '''12 THERAPISTS'''
        #print(f"\nForma Am per il livello {livello + 1}: {twelve_Am_livello.shape}")  # Debugging

        # Ora, per ogni indice relativo a un canale EEG...
        for ch_idx, ch in enumerate(canali_di_interesse):

            '''ALL THERAPISTS'''
            # Mi stampo il valore dei primi 5 campioni associato ai canali EEG
            print(f"Canale: \033[1m{nomi_canali[ch_idx]}\033[0m, Dati: {Am_livello[ch_idx, :5]}")  # Stampa i primi 5 campioni per verifica
            
            '''12 THERAPISTS'''
            # Mi stampo il valore dei primi 5 campioni associato ai canali EEG
            #print(f"Canale: \033[1m{nomi_canali[ch_idx]}\033[0m, Dati: {twelve_Am_livello[ch_idx, :5]}")  # Stampa i primi 5 campioni per verifica
            
            # Scegli l'asse giusto
            ax = axs[ch_idx, i]

            '''ALL THERAPISTS'''
            # Plot delle ricostruzioni per il canale corrente
            ax.plot(asse_x_ms, Am_livello[ch_idx, :], color=colore, alpha=0.7, label=f'{condizione}')

            '''12 THERAPISTS'''
            # Plot delle ricostruzioni per il canale corrente
            #ax.plot(asse_x_ms, twelve_Am_livello[ch_idx, :], color=colore, alpha=0.7, label=f'{condizione}')

            '''Aggiunta deviazione standard come area ombreggiata per tutte condizioni sperimentali: PER PLOT CON STD'''
            # Aggiungi la deviazione standard come area ombreggiata intorno alla linea media
            
            ax.fill_between(asse_x_ms, 
                            Am_livello[ch_idx, :] - std_livello[ch_idx, :], 
                            Am_livello[ch_idx, :] + std_livello[ch_idx, :], 
                            color = colore, alpha=0.3)  # Ombreggiatura con trasparenza
            
            ax.set_title(f'Livello {livello + 1} - Canale {nomi_canali[ch_idx]}')
            if i == 0:
                ax.set_ylabel(f'Voltaggio (µV)')
            if ch_idx == len(canali_di_interesse) - 1:
                ax.set_xlabel('Tempo (ms)')

            # Aggiungi una linea verticale per indicare il periodo di pre-stimolo
            ax.axvline(x=0, color='black', linestyle='--')  # 0 ms corrisponde all'inizio del pre-stimolo

# Aggiungi le legende fuori dai plot
handles, labels = [], []
for ax in axs.flatten():
    for handle, label in zip(*ax.get_legend_handles_labels()):
        if label not in labels:
            handles.append(handle)
            labels.append(label)

# Prova a mettere la legenda dentro la figura, in alto a sinistra
fig.legend(handles, labels, loc = 'upper center', bbox_to_anchor = (0.5, 0.05), ncol = 4, fontsize = 'large')

plt.tight_layout(rect=[0, 0.08, 1, 0.95])  # Aggiunge spazio per il titolo e la legenda
plt.show()

'''ALL THERAPISTS'''
# Salva la figura
#fig.savefig('/home/stefano/Interrogait/Analyses_EEG_1_20/ricostruzione_coefficienti_approssimazione_media_terapisti.png', bbox_inches='tight')

'''TWELVE THERAPISTS'''
# Salva la figura
#fig.savefig('/home/stefano/Interrogait/Analyses_EEG_1_20/ricostruzione_coefficienti_approssimazione_media_12_terapisti.png', bbox_inches='tight')


## STEP 4.3.2.3.2 Wavelet Analysis: Plot All Subjects For Coupled Experimental Conditions

In [ ]:
#Confronto tra le diverse condizioni sperimentali BASELINE vs ALL, CON BARRE DI ERRORE

'''BASELINE vs ALL'''

# CON BARRE DI ERRORE 

import matplotlib.pyplot as plt
import numpy as np

# Condizioni da confrontare con 'baseline'
condizioni_confronto = ['th_resp', 'vision_resp', 'shared_resp']

# Canali di interesse e loro nomi
canali_di_interesse = [12, 30, 48]  # Indici di Fz, Cz, Pz
nomi_canali = ['Fz', 'Cz', 'Pz']

# Livelli di decomposizione di interesse (penultimo e ultimo livello)
livelli_di_decomposizione = [3, 4]  # Indici dei livelli 4 e 5

# Colori per le condizioni sperimentali
colori_condizioni = {
    'baseline': 'green',
    'th_resp': 'blue',
    'vision_resp': 'purple',
    'shared_resp': 'red'
}

# Crea la figura con tante righe e 3 colonne (una per ciascun canale)
fig, axs = plt.subplots(len(condizioni_confronto) * len(livelli_di_decomposizione), len(canali_di_interesse), figsize=(25, 25), sharex=True, sharey=True)

'''ALL THERAPISTS'''
#fig.suptitle('Confronto a Coppie Alternato (Baseline vs Altre Exp Conditions) per Canali e Livelli di Decomposizione', fontsize=16)

'''TWELVE THERAPISTS'''
fig.suptitle('Confronto a Coppie Alternato (Baseline vs Altre Exp Conditions - 12 Therapists) per Canali e Livelli di Decomposizione', fontsize=16)

# Creazione dell'asse x in millisecondi (per 300 campioni, 1.2 secondi di durata)
asse_x_ms = np.linspace(-200, 1000, 300)  # Tempo in millisecondi, da -200ms a 1000ms

# Itera su ciascun confronto
for cond_idx, condizione in enumerate(condizioni_confronto):

    '''ALL THERAPISTS
    
    # Prendi i dati per baseline e la condizione corrente
    baseline_data = global_mean_results['baseline']['global_Am_mean']
    cond_data = global_mean_results[condizione]['global_Am_mean']
    
    # Devi avere anche i dati di deviazione standard
    baseline_std = global_mean_results['baseline']['global_Am_std']
    cond_std = global_mean_results[condizione]['global_Am_std']
    '''
    
    '''TWELVE THERAPISTS'''
    
    # Prendi i dati per baseline e la condizione corrente
    twelve_baseline_data = twelve_global_mean_results['baseline']['twelve_global_Am_mean']
    twelve_cond_data = twelve_global_mean_results[condizione]['twelve_global_Am_mean']
    
    # Devi avere anche i dati di deviazione standard
    twelve_baseline_std = twelve_global_mean_results['baseline']['twelve_global_Am_std']
    twelve_cond_std = twelve_global_mean_results[condizione]['twelve_global_Am_std']


    # Itera su ciascun livello di decomposizione (penultimo e ultimo)
    for livello_idx, livello in enumerate(livelli_di_decomposizione):
        
        # Itera su ciascun canale
        for col_idx, (canale_idx, canale_nome) in enumerate(zip(canali_di_interesse, nomi_canali)):
            
            # Calcola l'indice della riga corretta per il subplot
            row_idx = cond_idx * len(livelli_di_decomposizione) + livello_idx
            ax = axs[row_idx, col_idx]

            '''ALL THERAPISTS
            
            # Estrai i dati per baseline e condizione corrente al livello specificato
            baseline_livello = baseline_data[canale_idx, :, livello]
            cond_livello = cond_data[canale_idx, :, livello]
            baseline_std_livello = baseline_std[canale_idx, :, livello]
            cond_std_livello = cond_std[canale_idx, :, livello]

            '''

            '''TWELVE THERAPISTS'''
            
            # Estrai i dati per baseline e condizione corrente al livello specificato
            twelve_baseline_livello = twelve_baseline_data[canale_idx, :, livello]
            twelve_cond_livello = twelve_cond_data[canale_idx, :, livello]
            twelve_baseline_std_livello = twelve_baseline_std[canale_idx, :, livello]
            twelve_cond_std_livello = twelve_cond_std[canale_idx, :, livello]

            '''
            ALL THERAPISTS
            
            # Ombreggia l'errore con trasparenza per baseline e condizione corrente
            ax.fill_between(asse_x_ms, baseline_livello - baseline_std_livello, baseline_livello + baseline_std_livello,
                            color=colori_condizioni['baseline'], alpha=0.1)  # Trasparenza 0.1
            ax.fill_between(asse_x_ms, cond_livello - cond_std_livello, cond_livello + cond_std_livello,
                            color=colori_condizioni[condizione], alpha=0.1)  # Trasparenza 0.1
           
            # Traccia le linee per baseline e condizione corrente
            ax.plot(asse_x_ms, baseline_livello, color=colori_condizioni['baseline'], linestyle='-', linewidth=1, label=f'Baseline - Livello {livello + 1}')
            ax.plot(asse_x_ms, cond_livello, color=colori_condizioni[condizione], linestyle='--', linewidth=1, label=f'{condizione} - Livello {livello + 1}')
            '''
            
            '''TWELVE THERAPISTS'''
            # Ombreggia l'errore con trasparenza per baseline e condizione corrente
            ax.fill_between(asse_x_ms, twelve_baseline_livello - twelve_baseline_std_livello, twelve_baseline_livello + twelve_baseline_std_livello,
                            color=colori_condizioni['baseline'], alpha = 0.1)  # Trasparenza 0.1
            ax.fill_between(asse_x_ms, twelve_cond_livello - twelve_cond_std_livello, twelve_cond_livello + twelve_cond_std_livello,
                            color=colori_condizioni[condizione], alpha = 0.1)  # Trasparenza 0.1

            # Traccia le linee per baseline e condizione corrente
            ax.plot(asse_x_ms, twelve_baseline_livello, color=colori_condizioni['baseline'], linestyle='-', linewidth=1, label=f'Baseline - Livello {livello + 1}')
            ax.plot(asse_x_ms, twelve_cond_livello, color=colori_condizioni[condizione], linestyle='--', linewidth=1, label=f'{condizione} - Livello {livello + 1}')
            

            # Imposta i titoli e le etichette
            ax.set_title(f'{canale_nome} - Baseline vs {condizione} - Livello {livello + 1}')
            if col_idx == 0:
                ax.set_ylabel('Voltaggio (µV)')
            if row_idx == len(condizioni_confronto) * len(livelli_di_decomposizione) - 1:
                ax.set_xlabel('Tempo (ms)')

            # Aggiungi linea verticale a 0 ms per indicare l'inizio dello stimolo
            ax.axvline(x=0, color='black', linestyle='--')

            # Aggiungi legenda per ogni subplot con riferimento ai colori delle forme d'onda tracciate
            if row_idx == 0:  # Mostra la legenda solo nel primo subplot di ogni riga
                ax.legend(loc='upper right')

# Aggiusta layout
plt.tight_layout(rect=[0, 0.08, 1, 0.95])
plt.show()

# Salva la figura

'''ALL THERAPISTS'''
#fig.savefig('/home/stefano/Interrogait/Analyses_EEG_1_20/confronto_vision_resp_vs_exp_conditions_3channels.png', bbox_inches='tight')

'''ALL THERAPISTS MEAN & STD'''
#fig.savefig('/home/stefano/Interrogait/Analyses_EEG_1_20/confronto_vision_resp_vs_exp_conditions_3channels_mean_std.png', bbox_inches='tight')

'''TWELVE THERAPISTS MEAN & STD'''
#fig.savefig('/home/stefano/Interrogait/Analyses_EEG_1_20/confronto_12_therapists_baseline_vs_exp_conditions_3channels_mean_std.png', bbox_inches='tight')


In [ ]:
#Confronto tra le diverse condizioni sperimentali

'''VISION RESP vs ALL'''


import matplotlib.pyplot as plt
import numpy as np

# Condizioni da confrontare con 'vision_resp'
condizioni_confronto = ['baseline', 'th_resp', 'shared_resp']

# Canali di interesse e loro nomi
canali_di_interesse = [12, 30, 48]  # Indici di Fz, Cz, Pz
nomi_canali = ['Fz', 'Cz', 'Pz']

# Livelli di decomposizione di interesse (penultimo e ultimo livello)
livelli_di_decomposizione = [3, 4]  # Indici dei livelli 4 e 5

# Colori per le condizioni sperimentali
colori_condizioni = {
    'baseline': 'green',
    'th_resp': 'blue',
    'vision_resp': 'purple',
    'shared_resp': 'red'
}

# Crea la figura con tante righe e 3 colonne (una per ciascun canale)
fig, axs = plt.subplots(len(condizioni_confronto) * len(livelli_di_decomposizione), len(canali_di_interesse), figsize=(20, 20), sharex=True, sharey=True)
fig.suptitle('Confronto a Coppie Alternato (Vision_Resp vs Altre Exp Conditions) per Canali e Livelli di Decomposizione', fontsize=16)

# Creazione dell'asse x in millisecondi (per 300 campioni, 1.2 secondi di durata)
asse_x_ms = np.linspace(-200, 1000, 300)  # Tempo in millisecondi, da -200ms a 1000ms

# Itera su ciascun confronto
for cond_idx, condizione in enumerate(condizioni_confronto):
    # Prendi i dati per vision_resp e la condizione corrente
    vision_data = global_mean_results['vision_resp']['global_Am_mean']
    cond_data = global_mean_results[condizione]['global_Am_mean']
    
    # Itera su ciascun livello di decomposizione (penultimo e ultimo)
    for livello_idx, livello in enumerate(livelli_di_decomposizione):
        # Itera su ciascun canale
        for col_idx, (canale_idx, canale_nome) in enumerate(zip(canali_di_interesse, nomi_canali)):
            # Calcola l'indice della riga corretta per il subplot
            row_idx = cond_idx * len(livelli_di_decomposizione) + livello_idx
            ax = axs[row_idx, col_idx]

            # Estrai i dati per vision_resp e condizione corrente al livello specificato
            vision_livello = vision_data[canale_idx, :, livello]
            cond_livello = cond_data[canale_idx, :, livello]

            # Traccia le linee per vision_resp e condizione corrente con i colori specificati
            ax.plot(asse_x_ms, vision_livello, label=f'Vision_resp - Livello {livello + 1}', linestyle='-', color=colori_condizioni['vision_resp'])
            ax.plot(asse_x_ms, cond_livello, label=f'{condizione} - Livello {livello + 1}', linestyle='--', color=colori_condizioni[condizione])

            # Imposta i titoli e le etichette
            ax.set_title(f'{canale_nome} - Vision_Resp vs {condizione} - Livello {livello + 1}')
            if col_idx == 0:
                ax.set_ylabel('Voltaggio (µV)')
            if row_idx == len(condizioni_confronto) * len(livelli_di_decomposizione) - 1:
                ax.set_xlabel('Tempo (ms)')

            # Aggiungi linea verticale a 0 ms per indicare l'inizio dello stimolo
            ax.axvline(x=0, color='black', linestyle='--')

            # Aggiungi legenda per ogni subplot con riferimento ai colori delle forme d'onda tracciate
            ax.legend(loc='upper right')

# Aggiusta layout
plt.tight_layout(rect=[0, 0.08, 1, 0.95])
plt.show()

# Salva la figura
#fig.savefig('/home/stefano/Interrogait/Analyses_EEG_1_20/confronto_vision_resp_vs_exp_conditions_3channels.png', bbox_inches='tight')


In [ ]:
#Confronto tra le diverse condizioni sperimentali VISION RESP vs ALL, CON BARRE DI ERRORE

'''VISION RESP vs ALL'''

# CON BARRE DI ERRORE 

import matplotlib.pyplot as plt
import numpy as np

# Condizioni da confrontare con 'vision_resp'
condizioni_confronto = ['baseline', 'th_resp', 'shared_resp']

# Canali di interesse e loro nomi
canali_di_interesse = [12, 30, 48]  # Indici di Fz, Cz, Pz
nomi_canali = ['Fz', 'Cz', 'Pz']

# Livelli di decomposizione di interesse (penultimo e ultimo livello)
livelli_di_decomposizione = [3, 4]  # Indici dei livelli 4 e 5

# Colori per le condizioni sperimentali
colori_condizioni = {
    'baseline': 'green',
    'th_resp': 'blue',
    'vision_resp': 'purple',
    'shared_resp': 'red'
}

# Crea la figura con tante righe e 3 colonne (una per ciascun canale)
fig, axs = plt.subplots(len(condizioni_confronto) * len(livelli_di_decomposizione), len(canali_di_interesse), figsize=(25, 25), sharex=True, sharey=True)

'''ALL THERAPISTS'''
#fig.suptitle('Confronto a Coppie Alternato (Vision_Resp vs Altre Exp Conditions) per Canali e Livelli di Decomposizione', fontsize=16)


'''TWELVE THERAPISTS'''
fig.suptitle('Confronto a Coppie Alternato (Vision_Resp vs Altre Exp Conditions - 12 Therapists) per Canali e Livelli di Decomposizione', fontsize=16)


# Creazione dell'asse x in millisecondi (per 300 campioni, 1.2 secondi di durata)
asse_x_ms = np.linspace(-200, 1000, 300)  # Tempo in millisecondi, da -200ms a 1000ms

# Itera su ciascun confronto
for cond_idx, condizione in enumerate(condizioni_confronto):


    '''ALL THERAPISTS
    
    # Prendi i dati per vision_resp e la condizione corrente
    vision_data = global_mean_results['vision_resp']['global_Am_mean']
    cond_data = global_mean_results[condizione]['global_Am_mean']
    
    # Devi avere anche i dati di deviazione standard
    vision_std = global_mean_results['vision_resp']['global_Am_std']
    cond_std = global_mean_results[condizione]['global_Am_std']

    '''

    '''TWELVE THERAPISTS'''

    # Prendi i dati per vision_resp e la condizione corrente
    twelve_vision_data = twelve_global_mean_results['vision_resp']['twelve_global_Am_mean']
    twelve_cond_data = twelve_global_mean_results[condizione]['twelve_global_Am_mean']
    
    # Devi avere anche i dati di deviazione standard
    twelve_vision_std = twelve_global_mean_results['vision_resp']['twelve_global_Am_std']
    twelve_cond_std = twelve_global_mean_results[condizione]['twelve_global_Am_std']

    
    # Itera su ciascun livello di decomposizione (penultimo e ultimo)
    for livello_idx, livello in enumerate(livelli_di_decomposizione):
        
        # Itera su ciascun canale
        for col_idx, (canale_idx, canale_nome) in enumerate(zip(canali_di_interesse, nomi_canali)):
            
            # Calcola l'indice della riga corretta per il subplot
            row_idx = cond_idx * len(livelli_di_decomposizione) + livello_idx
            ax = axs[row_idx, col_idx]

            '''
            ALL THERAPISTS
            
            # Estrai i dati per vision_resp e condizione corrente al livello specificato
            vision_livello = vision_data[canale_idx, :, livello]
            cond_livello = cond_data[canale_idx, :, livello]
            vision_std_livello = vision_std[canale_idx, :, livello]
            cond_std_livello = cond_std[canale_idx, :, livello]
            '''

            '''TWELVE THERAPISTS'''

            # Estrai i dati per vision_resp e condizione corrente al livello specificato
            twelve_vision_livello = twelve_vision_data[canale_idx, :, livello]
            twelve_cond_livello = twelve_cond_data[canale_idx, :, livello]
            twelve_vision_std_livello = twelve_vision_std[canale_idx, :, livello]
            twelve_cond_std_livello = twelve_cond_std[canale_idx, :, livello]


            '''
            ALL THERAPISTS
            # Ombreggia l'errore con trasparenza per vision_resp e condizione corrente
            ax.fill_between(asse_x_ms, vision_livello - vision_std_livello, vision_livello + vision_std_livello,
                            color=colori_condizioni['vision_resp'], alpha=0.08)  # Trasparenza 0.1
            ax.fill_between(asse_x_ms, cond_livello - cond_std_livello, cond_livello + cond_std_livello,
                            color=colori_condizioni[condizione], alpha=0.08)  # Trasparenza 0.1

            # Traccia le linee per vision_resp e condizione corrente
            ax.plot(asse_x_ms, vision_livello, color=colori_condizioni['vision_resp'], linestyle='-', linewidth=1, label=f'Vision_resp - Livello {livello + 1}')
            ax.plot(asse_x_ms, cond_livello, color=colori_condizioni[condizione], linestyle='--', linewidth=1, label=f'{condizione} - Livello {livello + 1}')
            '''

            '''TWELVE THERAPISTS'''

             # Ombreggia l'errore con trasparenza per vision_resp e condizione corrente
            ax.fill_between(asse_x_ms, twelve_vision_livello - twelve_vision_std_livello, twelve_vision_livello + twelve_vision_std_livello,
                            color=colori_condizioni['vision_resp'], alpha=0.08)  # Trasparenza 0.1
            ax.fill_between(asse_x_ms, twelve_cond_livello - twelve_cond_std_livello, twelve_cond_livello + twelve_cond_std_livello,
                            color=colori_condizioni[condizione], alpha=0.08)  # Trasparenza 0.1

            # Traccia le linee per vision_resp e condizione corrente
            ax.plot(asse_x_ms, twelve_vision_livello, color=colori_condizioni['vision_resp'], linestyle='-', linewidth=1, label=f'Vision_resp - Livello {livello + 1}')
            ax.plot(asse_x_ms, twelve_cond_livello, color=colori_condizioni[condizione], linestyle='--', linewidth=1, label=f'{condizione} - Livello {livello + 1}')

            # Imposta i titoli e le etichette
            ax.set_title(f'{canale_nome} - Vision_Resp vs {condizione} - Livello {livello + 1}')
            if col_idx == 0:
                ax.set_ylabel('Voltaggio (µV)')
            if row_idx == len(condizioni_confronto) * len(livelli_di_decomposizione) - 1:
                ax.set_xlabel('Tempo (ms)')

            # Aggiungi linea verticale a 0 ms per indicare l'inizio dello stimolo
            ax.axvline(x=0, color='black', linestyle='--')

            # Aggiungi legenda per ogni subplot con riferimento ai colori delle forme d'onda tracciate
            if row_idx == 0:  # Mostra la legenda solo nel primo subplot di ogni riga
                ax.legend(loc='upper right')

# Aggiusta layout
plt.tight_layout(rect=[0, 0.08, 1, 0.95])
plt.show()

# Salva la figura

'''ALL THERAPISTS'''
#fig.savefig('/home/stefano/Interrogait/Analyses_EEG_1_20/confronto_vision_resp_vs_exp_conditions_3channels.png', bbox_inches='tight')

'''ALL THERAPISTS MEAN & STD'''
#fig.savefig('/home/stefano/Interrogait/Analyses_EEG_1_20/confronto_vision_resp_vs_exp_conditions_3channels_mean_std.png', bbox_inches='tight')


'''TWELVE THERAPISTS MEAN & STD'''
#fig.savefig('/home/stefano/Interrogait/Analyses_EEG_1_20/confronto_12_therapists_vision_resp_vs_exp_conditions_3channels_mean_std.png', bbox_inches='tight')



In [ ]:
for labels in [labels_terapeuta[0]]:
    print(labels)
print()
print(type(dati_terapeuta))
print()
print(labels_terapeuta[0].astype(np.int32))

In [ ]:
#Verifico il tipo di "dati_terapeuta" e "labels_terapeuta" di tutti i soggetti (solo terapisti) 
print(f"\033[1mdati_terapeuta\033[0m:' {type(dati_terapeuta)}")
print(f"\033[1mlabels_terapeuta\033[0m:' {type(labels_terapeuta)}")

In [ ]:
# Concatenare lungo la prima dimensione

print(f"Concateno i dati di \033[1mtutti i terapisti\033[0m!\n")

#idx = 5  
#x_all = dati_terapeuta[idx]
#y_all = labels_terapeuta[idx]

x_all = np.concatenate(dati_terapeuta, axis=0)
y_all = np.concatenate(labels_terapeuta, axis = 0)
print('dati shape totali: ', x_all.shape)
print('labels shape totali: ', y_all.shape)

In [ ]:
#x_all.shape[0]

In [ ]:
#Standardizzimo i dati

import numpy as np

# Calcola la media e la deviazione standard di ogni canale
mean_per_channel = np.mean(x_all, axis=(0, 2), keepdims=True)
std_per_channel = np.std(x_all, axis=(0, 2), keepdims=True)

# Standardizza i dati dividendo per la deviazione standard e sottraendo la media
x_all_standardized = (x_all - mean_per_channel) / std_per_channel

# Verifica delle forme dopo la standardizzazione
print('Shape dei dati standardizzati:', x_all_standardized.shape)


In [ ]:
#plt.plot(x_all[0].T)
#plt.plot(x_all_standardized[0].T)

In [ ]:
# Vedo il tipo di un elemento dentro le X e le Y 

print(f"\t\t\t\033[1mBefore\033[0m")
print(f"tipo di x_all:  {type(x_all)},\tun elemento di x_all: {x_all.dtype}")
print(f"tipo di y_all: {type(y_all)}, \tun elemento di y_all:  \033[1m{y_all.dtype}\033[0m")

#Converto le labels in 'int'
print(f"\n\t\t\t\033[1mAfter\033[0m")
y_all = y_all.astype(int) 

print(f"tipo di x_all:  {type(x_all)},\tun elemento di x_all: {x_all.dtype}")
print(f"tipo di y_all: {type(y_all)}, \tun elemento di y_all:  \033[1m{y_all.dtype}\033[0m")



In [ ]:
#Labels 

# Controllo se ci sono valori al di fuori dell'intervallo previsto
valori_al_di_fuori = (torch.tensor(y_all) < 0) | (torch.tensor(y_all) > 2)

if torch.any(valori_al_di_fuori):
    print("Ci sono valori al di fuori dell'intervallo previsto (0, 1, 2):")
    print(y_all[valori_al_di_fuori])
else:
    print("Tutte le etichette sono nell'intervallo previsto (0, 1, 2).")
print()

# Stampiamo le etichette e il loro tipo di dati
#print("Etichette:", x)
print()
print(f"Tipo dei miei \033[1mdati\033[0m:", x_all.dtype)
print()
print(f"Etichette {y_all}")
print()
print(f"Tipo delle mie \033[1metichette\033[0m: {y_all.dtype}")

In [ ]:
# Trasforma i tuoi dati e le etichette in Tensori PyTorch
x = torch.tensor(x_all_standardized).float()
y = torch.tensor(y_all.astype(np.int32)).long()

# Creazione di TensorDataset con i dati per il terapeuta e le relative etichette
dataset = TensorDataset(x, y)

# Divisione del dataset in set di train e test
train_idx, test_idx = train_test_split(range(len(dataset)), test_size = 0.2, random_state = 42)

# Divisione del dataset in set di train e validation
train_idx, val_idx = train_test_split(train_idx, test_size = 0.2, random_state = 42)

#Prendo indici dei valori dei dati corrispondenti e li inserisco dentro data.Subset 
train_dataset = torch.utils.data.Subset(dataset, train_idx)
test_dataset = torch.utils.data.Subset(dataset, test_idx)
val_dataset =  torch.utils.data.Subset(dataset, val_idx)

# Definizione dei DataLoader per il set di addestramento e di test
batch_size = 64

#Inserisco i dati nei vari DataLoader
train_loader = DataLoader(dataset = train_dataset, batch_size = batch_size, shuffle = True)
test_loader = DataLoader(dataset = test_dataset, batch_size = batch_size, shuffle = False)
val_loader = DataLoader(dataset = val_dataset, batch_size = batch_size, shuffle = False)


In [ ]:
# Itera attraverso il DataLoader per ottenere la forma dei singoli batch
for batch in train_loader:
    batch_shape_tr = batch[0].shape  # Consideriamo solo il primo elemento del batch
    print("Forma del batch train:", batch_shape_tr)
    break  # Interrompi dopo il primo batch per evitare di stampare tutti i batch

for batch in test_loader:
    batch_shape_ts = batch[0].shape  # Consideriamo solo il primo elemento del batch
    print("Forma del batch test:", batch_shape_ts)
    break  # Interrompi dopo il primo batch per evitare di stampare tutti i batch

In [ ]:
#Calcolo proporzione delle etichette per le classi

label_counts = np.unique(y_all, return_counts = True)[1]

# Calcola il numero totale di etichette
total_labels = len(y_all)

# Calcola la percentuale di ciascuna classe
class_proportions = label_counts / total_labels * 100

# Stampa le percentuali delle classi
for label, proportion in enumerate(class_proportions):
    print(f"\033[1mClasse {label}\033[0m: {proportion:.2f}%")


In [ ]:
# Le percentuali delle classi che ho
class_proportions = [36.90, 25.60, 37.51]

# Calcola i pesi delle classi come l'inverso delle proporzioni
class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

# Normalizza i pesi in modo che la somma sia uguale al numero delle classi
class_weights /= class_weights.sum()
print(class_weights)

## STEP 5: Decoding in sensor space: mne.decoding.SlidingEstimator

In MNE c'è un oggetto chiamato **mne.decoding.SlidingEstimator** 
[https://mne.tools/stable/generated/mne.decoding.SlidingEstimator.html#mne.decoding.SlidingEstimator]

che consente di testare, per ogni instante temporale (campione EEG) sugli i-esimi canali della medesima finestra considerata, il grado di accuratezza nella classificazione delle condizioni del protocollo sperimentale che si ha.

link[https://mne.tools/stable/auto_examples/decoding/decoding_spatio_temporal_source.html#sphx-glr-auto-examples-decoding-decoding-spatio-temporal-source-py] 


L'idea è che applica una procedura iterativa per lo stesso punto temporale di ogni i-esimo canale EEG per la medesima finestra, e lo considera come input data per predire la condizione sperimentale di interesse.

Alla fine, si avrà un grafico nella nostra finestra EEG quali porzioni di punti temporali EEG siano maggiormente discriminativi nel processo di decodifica del nostro stato mentale.

Si potrebbero importare dei modelli da **Scikit-Learn** per fare prove con modelli diversi: https://scikit-learn.org/stable/supervised_learning.html


### STEP 5.1 - Single Therapist EEG Data Reconstructions

Tu sai che **all_subjects_condition_results** ha questi dizionari

dict_keys

(['wave_baseline_1', 'wave_th_resp_1', 'wave_vision_resp_1', 'wave_shared_resp_1', 
'wave_baseline_2', 'wave_vision_resp_2', 'wave_th_resp_2', 'wave_shared_resp_2', 
'wave_baseline_3', 'wave_th_resp_3', 'wave_vision_resp_3', 'wave_shared_resp_3', 
'wave_shared_resp_4', 'wave_vision_resp_4', 'wave_th_resp_4', 'wave_baseline_4', 
'wave_baseline_5', 'wave_th_resp_5', 'wave_vision_resp_5', 'wave_shared_resp_5', 
'wave_baseline_6', 'wave_th_resp_6', 'wave_vision_resp_6', 'wave_shared_resp_6', 
'wave_baseline_7', 'wave_th_resp_7', 'wave_vision_resp_7', 'wave_shared_resp_7', 
'wave_baseline_8', 'wave_th_resp_8', 'wave_shared_resp_8', 'wave_vision_resp_8', 
'wave_baseline_9', 'wave_th_resp_9', 'wave_vision_resp_9', 'wave_shared_resp_9', 
'wave_baseline_10', 'wave_th_resp_10', 'wave_vision_resp_10', 'wave_shared_resp_10', 
'wave_baseline_11', 'wave_th_resp_11', 'wave_vision_resp_11', 'wave_shared_resp_11', 
'wave_baseline_12', 'wave_th_resp_12', 'wave_vision_resp_12', 'wave_shared_resp_12', 
'wave_shared_resp_13', 'wave_th_resp_13', 'wave_vision_resp_13', 'wave_baseline_13', 
'wave_th_resp_14', 'wave_baseline_14', 'wave_shared_resp_14', 'wave_vision_resp_14', 
'wave_vision_resp_15', 'wave_th_resp_15', 'wave_baseline_15', 'wave_shared_resp_15'])


dove **ciascuna** ha queste sotto-chiavi come valore:

dict_keys(['D', 'A', 'Dm', 'Am', 'D_std', 'A_std', 'A_labels'])

Di ogni **chiave di primo ordine** (i.e., 'wave_baseline_1', 'wave_th_resp_1', etc...) che ha come **suffisso '_1'** nel suo nome di chiave (**dati del 1° soggetto**), voglio prendere **solo i dati EEG** (i.e. ricostruzioni del segnale nel dominio del tempo) a partire dai coefficienti di approssimazione che son  del **4° e 5° livello di ricostruzione** (associati alle frequenze in **banda theta per il 4°** e **delta nel 5° livello**)...

Dovrei prendere, quindi, di ogni 'A' solo ultimo e penultimo livello di ricostruzione, sapendo che **la shape di A** è

- n° trials (variabile per la condizione sperimentale)
- n° canali EEG (61)
- n° campioni temporali per trials (300, corrispondenti ad 1.2s di pre-stimolo) 
- n°livello di ricostruzione (5)..

Quindi dovrei prendermi **per ogni condizione sperimentale del 1° soggetto**, 
La ricostruzione di ogni singolo trial (42), per alcuni canali solo (Fz, Cz e Pz, indicizzati con valori numerici --> [12, 30, 48]  # Indici di Fz, Cz, Pz), di quei 300 punti temporali per solo il 4 e 5 livello di ricostruzione...

<br>

Sapendo ad esempio che 

"all_subjects_condition_results['wave_baseline_1']['A'].shape"

è (42, 61, 300, 5)

in totale dovrei prendermi alla fine per ogni trial (42) solo gli ultimi 2 livelli della sua ricostruzione, per solo i canali EEG menzionati..

Quindi una cosa tipo: 

(42, [12, 30, 48], 300, -2:)

Inoltre vorrei anche crearmi dentro il **mio dizionario 'extracted_reconstructions'** (che posso rinominare 'first_th_reconstructions' per l'esempio del 1° soggetto) **due sotto-chiavi**, che voglio chiamare **'theta'** e **'delta'**, per metterci **per quello stesso trial le relative ricostruzioni** : 

- dentro **theta**, il 4° livello di ricostruzione
- dentro **delta**, il 5° livello di ricostruzione di quello stesso trial per quello stesso canale ...


### STEP 5.1.2 - Single Therapist EEG Data Extraction


Adesso **per il primo soggetto**, ho **estratto i dati e le labels** rispetto al **livello di ricostruzione**, per **ognuna delle condizioni sperimentali SEPARATAMENTE**

Ho creato una variabile **first_th_reconstructions** per appendergli i **dati** e le **labels** di **ogni condizione sperimentale** separatamente

N.B. "**first_th_reconstructions**" ha dict_keys(['wave_baseline_1', 'wave_th_resp_1', 'wave_vision_resp_1', 'wave_shared_resp_1']) ognuna ha **due sottochiavi** che son dict_keys(['theta', 'delta']) ed ognuna ha un **n° di dati e labels DIVERSO, a seconda della condizione sperimentale!**.

### STEP 5.1.2.1 - Single Therapist EEG Data Concatenation

Adesso **per questo primo soggetto**, vado a **concatenare i dati e le labels rispetto al livello di ricostruzione per tutte le condizioni sperimentali INSIEME**

Quindi iterando sulle chiavi di **first_th_reconstructions** accedo ai **dati** e **label** delle sotto-chiavi '**theta**' (o '**delta**') relativa ad **ogni condizione sperimentale** e li **concateno**, in modo che siano **ordinati sequenzialmente** (i.e., uno sotto l'altro) avendo la **stessa corrispondenza tra dati e label** 

N.B. "**first_th_reconstructions**" ha dict_keys(['wave_baseline_1', 'wave_th_resp_1', 'wave_vision_resp_1', 'wave_shared_resp_1']) ognuna ha **due sottochiavi** che son dict_keys(['theta', 'delta']) ed ognuna ha un **n° di dati e labels UGUALE (stesssa shape tra dati e labels!)**

### STEP 5.1.2.2 - Visualization of Single Trial for Therapist 1 for each level of reconstruction (θ+δ, θ and δ)

### STEP 5.2 - All Therapists EEG Data Reconstructions

#### Concatenazione All Single Subject Data (TH) per tutte le condizioni sperimentali, per ogni livello di ricostruzione (θ+δ, θ and δ)

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''

#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('all_subjects_condition_results_th.pkl', 'rb') as f:
#    all_subjects_condition_results_th = pickle.load(f)
    
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_all_subjects_condition_results_th.pkl', 'rb') as f:
    new_all_subjects_condition_results_th = pickle.load(f)

In [ ]:
new_all_subjects_condition_results_th.keys()

In [ ]:
#print(f"\033[1mChiavi di primo ordine\033[0m i.e., all_subjects_condition_results_th: \n\n{all_subjects_condition_results_th.keys()}")
#print(f"\n\n\033[1mChiavi di ogni condizione sperimentale\033[0m, i.e., 'wave_baseline_1': {all_subjects_condition_results_th['wave_baseline_1'].keys()}")

#all_subjects_condition_results['wave_baseline_1'].keys()


print(f"\033[1mChiavi di primo ordine\033[0m i.e., new_all_subjects_condition_results_th: \n\n{new_all_subjects_condition_results_th.keys()}")
print(f"\n\n\033[1mChiavi di ogni condizione sperimentale\033[0m, i.e., 'wave_baseline_1': {new_all_subjects_condition_results_th['wave_baseline_1'].keys()}")


In [ ]:
#new_all_subjects_condition_results_th['wave_baseline_1'].keys()
print(new_all_subjects_condition_results_th['wave_baseline_1']['A'].shape)
print(new_all_subjects_condition_results_th['wave_baseline_1']['D'].shape)

In [ ]:
'''
Da "all_subjects_condition_results" ottengo:

Le ricostruzioni 4° e 5° livello di tutti i terapisti per tutte le condizioni sperimentali dai coefficienti di approssimazione
Le ricostruzioni 5° livello di tutti i terapisti per tutte le condizioni sperimentali dai coefficienti di dettaglio

				(i.e., single_th_all_extracted_reconstructions):

'''

import numpy as np

# Definizione degli indici dei canali desiderati
selected_channels = [12, 30, 48]  # Indici per Fz, Cz, Pz

# Creazione di un dizionario dei dati di tutti i terapisti singolarmente, per salvare le ricostruzioni estratte per livello 4 e 5
#single_th_all_extracted_reconstructions = {}

new_single_th_all_extracted_reconstructions = {}

# Iterazione su tutte le condizioni sperimentali di tutti i soggetti 

#'OLD VERSION'
#for condition, data in all_subjects_condition_results_th.items():

for condition, data in new_all_subjects_condition_results_th.items():
    
    # Estrarre le etichette per questa condizione
    A_labels = data['A_labels']
    
    # Estrazione della matrice 'A' per le ricostruzioni del segnale con coefficienti di approssimazione
    A = data['A']
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Estrazione della matrice 'D' per le ricostruzioni del segnale con coefficienti di approssimazione
    D = data['D']
    
    # Estrarre solo i canali selezionati e i livelli di ricostruzione desiderati (4° e 5°, quindi indice -2 e -1)
    theta_reconstruction = A[:, selected_channels, :, -2]  # 4° livello di ricostruzione
    delta_reconstruction = A[:, selected_channels, :, -1]  # 5° livello di ricostruzione
    
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Ottenere i coefficienti di dettaglio del 5° livello di ricostruzione (theta range)
    coeff_fifth_detail_theta = D[:, selected_channels, :, -1]  # Coefficienti di dettaglio del livello 5
    
    
    # Trasponi per ottenere la forma desiderata: (trials, canali, punti temporali)
    theta_reconstruction = theta_reconstruction.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    delta_reconstruction = delta_reconstruction.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    coeff_fifth_detail_theta = coeff_fifth_detail_theta.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Creare un sotto-dizionario per organizzare 
    #le ricostruzioni EEG del livello 4 'theta' e livello 5 'delta' dai coeff di approx
    #le ricostruzioni EEG del livello 4 'theta' e livello 5 'delta' dai coeff di detail
    
    new_single_th_all_extracted_reconstructions[condition] = {
        'theta': theta_reconstruction,
        'delta': delta_reconstruction,
        'coeff_fifth_detail_theta': coeff_fifth_detail_theta, 
        'labels': A_labels
    }

# Verifica delle dimensioni del risultato estratto per una condizione specifica
print(f"\t\t\033[1mRicostruzioni 4° e 5° livello di tutti i terapisti per tutte le condizioni sperimentali")
#print(f"\n\n\t\t\t\t(i.e., \033[1msingle_th_all_extracted_reconstructions\033[0m):\n")

print(f"\n\n\t\t\t\t(i.e., \033[1mnew_single_th_all_extracted_reconstructions\033[0m):\n")


#for condition, extracted_data in single_th_all_extracted_reconstructions.items():

#'''AGGIUNTI COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''

for condition, extracted_data in new_single_th_all_extracted_reconstructions.items():
    
    print(f"Condizione: \033[1m{condition}\033[0m, "
          f"Theta shape: \033[1m{extracted_data['theta'].shape}\033[0m, "
          f"Delta shape: \033[1m{extracted_data['delta'].shape}\033[0m, "
          f"Coeff Fifth Detail shape: \033[1m{extracted_data['coeff_fifth_detail_theta'].shape}\033[0m, "
          f"Labels: \033[1m{len(extracted_data['labels'])}\033[0m")

# STEP 2: Concatenare i dati e le etichette di tutti i soggetti per i livelli di ricostruzione 4 e 5

# Inizializzazione delle liste per raccogliere i dati e le etichette del 4° e 5° livello di ricostruzione da coeff approx

all_th_fourth = []
labels_th_fourth = []
exp_conditions_fourth = []

all_th_fifth = []
labels_th_fifth = []
exp_conditions_fifth = []


#'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''

all_th_fifth_detail = []
labels_th_fifth_detail = []
exp_conditions_fifth_detail = []

# Iterazione su tutte le condizioni sperimentali

#for condition, data in single_th_all_extracted_reconstructions.items():
for condition, data in new_single_th_all_extracted_reconstructions.items():    
    
    # Preparazione delle liste per dati e etichette per ogni condizione
    dati_fourth = [None] * 4  # Per 'baseline', 'th_resp', 'vision_resp', 'shared_resp'
    labels_fourth = [None] * 4
    
    dati_fifth = [None] * 4
    labels_fifth = [None] * 4
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    dati_fifth_detail = [None] * 4
    labels_fifth_detail = [None] * 4
    
    for chiave, valore in data.items():
        
        if chiave == 'theta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            if 'baseline' in condition:
                dati_fourth[0] = valore
                labels_fourth[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fourth[1] = valore
                labels_fourth[1] = data['labels']
            
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fourth[2] = valore
                labels_fourth[2] = data['labels']
                
            elif 'shared_resp' in condition:
                dati_fourth[3] = valore
                labels_fourth[3] = data['labels']
                
        elif chiave == 'delta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            if 'baseline' in condition:
                dati_fifth[0] = valore
                labels_fifth[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fifth[1] = valore
                labels_fifth[1] = data['labels']
            
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fifth[2] = valore
                labels_fifth[2] = data['labels']
                
                
            elif 'shared_resp' in condition:
                dati_fifth[3] = valore
                labels_fifth[3] = data['labels']
        
        elif chiave == 'coeff_fifth_detail_theta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            
            if 'baseline' in condition:
                dati_fifth_detail[0] = valore
                labels_fifth_detail[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fifth_detail[1] = valore
                labels_fifth_detail[1] = data['labels']
                
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fifth_detail[2] = valore
                labels_fifth_detail[2] = data['labels']
                
            elif 'shared_resp' in condition:
                dati_fifth_detail[3] = valore
                labels_fifth_detail[3] = data['labels']
                
            
    # Filtrare i valori non None
    dati_fourth = [d for d in dati_fourth if d is not None]
    labels_fourth = [l for l in labels_fourth if l is not None]
    
    dati_fifth = [d for d in dati_fifth if d is not None]
    labels_fifth = [l for l in labels_fifth if l is not None]
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    dati_fifth_detail = [d for d in dati_fifth_detail if d is not None]
    labels_fifth_detail = [l for l in labels_fifth_detail if l is not None]
    
    # Concatenare i dati e le etichette
    if dati_fourth:
        datas_fourth = np.concatenate(dati_fourth, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fourth = np.concatenate([np.array(l) for l in labels_fourth], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_th_fourth.append(datas_fourth)
        labels_th_fourth.append(labels_fourth)
        exp_conditions_fourth.append(condition)
    
    if dati_fifth:
        datas_fifth = np.concatenate(dati_fifth, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fifth = np.concatenate([np.array(l) for l in labels_fifth], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_th_fifth.append(datas_fifth)
        labels_th_fifth.append(labels_fifth)
        exp_conditions_fifth.append(condition)
    
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    if dati_fifth_detail:
        
        datas_fifth_detail = np.concatenate(dati_fifth_detail, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fifth_detail = np.concatenate([np.array(l) for l in labels_fifth_detail], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_th_fifth_detail.append(datas_fifth_detail)
        labels_th_fifth_detail.append(labels_fifth_detail)
        exp_conditions_fifth_detail.append(condition)

# STEP 3: Concatenazione finale di tutti i dati e le etichette

# Concatenazione finale di tutti i dati e le etichette

#'''PER COEFFICIENTI DI APPROSSIMAZIONE 4° LIVELLO (i.e., range 0-7.812Hz)'''
if all_th_fourth:
    all_fourth = np.concatenate(all_th_fourth, axis=0)
else:
    all_fourth = np.array([])

if labels_th_fourth:
    all_fourth_labels = np.concatenate(labels_th_fourth, axis=0)
else:
    all_fourth_labels = np.array([])

    
#'''PER COEFFICIENTI DI APPROSSIMAZIONE 5° LIVELLO (i.e., range 0-3.9Hz)'''    
if all_th_fifth:
    all_fifth = np.concatenate(all_th_fifth, axis=0)
else:
    all_fifth = np.array([])

if labels_th_fifth:
    all_fifth_labels = np.concatenate(labels_th_fifth, axis=0)
else:
    all_fifth_labels = np.array([])
    

#'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
if all_th_fifth_detail:
    all_fifth_detail = np.concatenate(all_th_fifth_detail, axis=0)
else:
    all_fifth_detail = np.array([])

if labels_th_fifth_detail:
    all_fifth_detail_labels = np.concatenate(labels_th_fifth_detail, axis=0)
else:
    all_fifth_detail_labels = np.array([])
    

# Verifica delle dimensioni del risultato finale
print(f"\n\n\n\t\tTUTTI I TRIAL DI TUTTI I SOGGETTI DI OGNI CONDIZIONE SPERIMENTALE - PER LIVELLO DI RICOSTRUZIONE ")

print(f"\n\033[1m4° livello\033[0m di ricostruzione da Coeff di Approx - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fourth\033[0m: \033[1m{all_fourth.shape}\033[0m, Length di \033[1mall_fourth_labels\033[0m: \033[1m{len(all_fourth_labels)}\033[0m")

print(f"\n\033[1m5° livello\033[0m di ricostruzione da Coeff di Approx - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fifth\033[0m: \033[1m{all_fifth.shape}\033[0m, Length di \033[1mall_fifth_labels\033[0m: \033[1m{len(all_fifth_labels)}\033[0m")

print(f"\n\033[1m5° livello\033[0m di ricostruzione da Coeff di Detail - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fifth_detail\033[0m: \033[1m{all_fifth_detail.shape}\033[0m, Length di \033[1mall_fifth_detail_labels\033[0m: \033[1m{len(all_fifth_detail_labels)}\033[0m")


In [ ]:
!pwd

In [ ]:
#Salvo ricostruzioni 4° e 5° livello per singolo terapista con concatenazioni dati e labels 

''' PATH  --> cd Plots_Sliding_Estimator_MNE '''

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('single_th_all_extracted_reconstructions.pkl', 'wb') as f:
#    pickle.dump(single_th_all_extracted_reconstructions, f)
    
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''

import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_single_th_all_extracted_reconstructions.pkl', 'wb') as f:
    pickle.dump(new_single_th_all_extracted_reconstructions, f)


In [ ]:
'''SALVO IN UN GRANDE DIZIONARIO I DATI E LE LABELS CONCATENATI DI TUTTI I SOGGETTI PER IL LIVELLO DI RICOSTRUZIONE'''


#Creo dizionario per le concatenazioni di dati e labels a seconda del livello di ricostruzione del segnale EEG 
new_all_th_concat_reconstructions = {'all_th_fourth': all_fourth, 
                                 'all_th_fourth_labels': all_fourth_labels,
                                 'all_th_fifth': all_fifth,
                                 'all_th_fifth_labels': all_fifth_labels,
                                 'all_th_fifth_detail': all_fifth_detail,
                                 'all_th_fifth_detail_labels': all_fifth_detail_labels
                                }

'''STAMPA DELLE CHIAVI e SHAPE'''
#all_th_concat_reconstructions.keys()
#all_th_concat_reconstructions['all_th_fourth'].shape
#all_th_concat_reconstructions['all_th_fourth_labels'].shape

#all_th_concat_reconstructions['all_th_fifth'].shape
#all_th_concat_reconstructions['all_th_fifth_labels'].shape



#all_th_concat_theta = {'all_th_fourth': all_fourth, 
#                       'all_th_fourth_labels': all_fourth_labels}


#all_th_concat_delta = {'all_th_fifth': all_fifth,
#                       'all_th_fifth_labels': all_fifth_labels}


#all_th_concat_theta.keys()
#all_th_concat_delta.keys()

In [ ]:
new_all_th_concat_reconstructions.keys()

In [ ]:
!pwd

In [ ]:
'''SALVO I DATI CONCATENATI DI TUTTI I SOGGETTI TERAPISTI, RISPETTO AD UNO SPECIFICO LIVELLO DI RICOSTRUZIONE'''

import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_fourth_th.pkl', 'wb') as f:
    pickle.dump(all_fourth, f) 


import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_fifth_th.pkl', 'wb') as f:
    pickle.dump(all_fifth, f) 

    
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_fifth_detail_th.pkl', 'wb') as f:
    pickle.dump(all_fifth_detail, f) 

'''SALVO I DATI CONCATENATI DI TUTTI I SOGGETTI TERAPISTI, RISPETTO AD OGNI LIVELLO DI RICOSTRUZIONE INSIEME'''
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_th_concat_reconstructions.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions, f)   

In [ ]:
#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_single_th_all_extracted_reconstructions.pkl', 'rb') as f:
#    new_single_th_all_extracted_reconstructions = pickle.load(f)

In [ ]:
#Dizionario con dati e labels 
#a seconda del livello di ricostruzione del segnale EEG 
#di ogni singolo soggetto 
#per tutte le condizioni sperimentali SEPARATAMENTE!

'''OLD'''
#print(f"\n\033[1msingle_th_all_extracted_reconstructions.keys()\033[0m: \n{single_th_all_extracted_reconstructions.keys()}\n")
#print(f"\n\033[1msingle_th_all_extracted_reconstructions['wave_baseline_1'].keys()\033[0m: {single_th_all_extracted_reconstructions['wave_baseline_1'].keys()}")


'''NEW'''
print(f"\n\033[1mnew_single_th_all_extracted_reconstructions.keys()\033[0m: \n{new_single_th_all_extracted_reconstructions.keys()}\n")
print(f"\n\033[1mnew_single_th_all_extracted_reconstructions['wave_baseline_1'].keys()\033[0m: {new_single_th_all_extracted_reconstructions['wave_baseline_1'].keys()}")


#single_th_all_extracted_reconstructions['wave_baseline_1']['theta'].shape
#single_th_all_extracted_reconstructions['wave_baseline_1']['delta'].shape
#len(single_th_all_extracted_reconstructions['wave_baseline_1']['labels'])

In [ ]:
# Itera su ogni chiave nel dizionario new_single_th_all_extracted_reconstructions
for main_key in new_single_th_all_extracted_reconstructions.keys():
    # Verifica se 'coeff_fifth_detail_theta' è presente tra le sottochiavi
    if 'coeff_fifth_detail_theta' not in new_single_th_all_extracted_reconstructions[main_key]:
        print(f"La chiave '{main_key}' \033[1mNON contiene\033[0m 'coeff_fifth_detail_theta'")
    else:
        print(f"La chiave '{main_key}' contiene 'coeff_fifth_detail_theta'")

In [ ]:
'''
Questa struttura consente di avere i dati correttamente organizzati e concatenati per ogni soggetto 
in base al livello di ricostruzione, 
mantenendo la corrispondenza tra dati e etichette per ogni condizione sperimentale

Da           "single_th_all_extracted_reconstructions"       a            "subject_level_concatenations_th"

Da           "new_single_th_all_extracted_reconstructions"       a       "new_subject_level_concatenations_th"
'''

import numpy as np

# Dizionario per contenere i dati concatenati per ogni soggetto e livello di ricostruzione
new_subject_level_concatenations_th = {}

# Variabile per tracciare il soggetto precedente
previous_subject_suffix = None

print(f"\t\t\033[1mConcatenazione dati 4° e 5° livello di OGNI terapista di TUTTE le condizioni sperimentali INSIEME\033[0m")
#print(f"\n\t\tda\t\033[1m'single_th_all_extracted_reconstructions'\033[0m \ta\t\033[1m'subject_level_concatenations_th'\033[0m")

print(f"\n\t\tda\t\033[1m'new_single_th_all_extracted_reconstructions'\033[0m \ta\t\033[1m'new_subject_level_concatenations_th'\033[0m")

# Iterazione su tutte le chiavi di single_th_all_extracted_reconstructions

#'''OLD VERSION'''
#for condition, data in single_th_all_extracted_reconstructions.items():

for condition, data in new_single_th_all_extracted_reconstructions.items():
    
    # Estrazione del suffisso numerico del soggetto (es. '1', '2', ...)
    subject_suffix = condition.split('_')[-1]  # Prende solo la parte numerica
    
    # Creazione del nome della chiave del soggetto specifico
    subj_name = f'th_{subject_suffix}'  # Crea la chiave con prefisso 'th_' e suffisso numerico
    
    # Se stiamo per passare a un nuovo soggetto, stampiamo le dimensioni delle concatenazioni per il soggetto precedente
    if previous_subject_suffix is not None and subject_suffix != previous_subject_suffix:
        
        print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('th_{previous_subject_suffix}'):\033[0m\n")
        prev_subject_name = f'th_{previous_subject_suffix}'
        
        #levels = subject_level_concatenations_th[prev_subject_name]
        
        levels = new_subject_level_concatenations_th[prev_subject_name]
        
        # Concatenazione dei dati prima della stampa
        theta_concat = np.concatenate(levels['theta'], axis=0)
        delta_concat = np.concatenate(levels['delta'], axis=0)
        
        #Coefficienti di dettaglio 5° livello theta
        theta_concat_strict = np.concatenate(levels['theta_strict'], axis=0)
        
        labels_concat = np.concatenate(levels['labels'], axis=0)
        
        #if 'coeff_fifth_detail_theta' not in levels:
        #    print(f"La chiave 'coeff_fifth_detail_theta' non è presente per il soggetto: {prev_subject_name}")

        print(f"Soggetto: \033[1m{prev_subject_name}\033[0m, "
              f"Theta shape: \033[1m{np.concatenate(levels['theta'], axis=0).shape}\033[0m, "
              f"Delta shape: \033[1m{np.concatenate(levels['delta'], axis=0).shape}\033[0m, "
              f"Theta Strict shape: \033[1m{np.concatenate(levels['theta_strict'], axis=0).shape}\033[0m, "
              f"Labels length: \033[1m{len(np.concatenate(levels['labels'], axis=0))}\033[0m")
        
        
        #'''OLD'''
        # Salvataggio dei dati concatenati nel dizionario come array NumPy
        #subject_level_concatenations_th[prev_subject_name]['theta'] = theta_concat
        #subject_level_concatenations_th[prev_subject_name]['delta'] = delta_concat
        #subject_level_concatenations_th[prev_subject_name]['labels'] = labels_concat
        
        
        #'''NEW'''
        new_subject_level_concatenations_th[prev_subject_name]['theta'] = theta_concat
        new_subject_level_concatenations_th[prev_subject_name]['delta'] = delta_concat
        
        new_subject_level_concatenations_th[prev_subject_name]['theta_strict'] = theta_concat_strict
        
        new_subject_level_concatenations_th[prev_subject_name]['labels'] = labels_concat
    
    #'''OLD'''
    # Inizializzare il dizionario per il soggetto specifico se non esiste già
    #if subj_name not in subject_level_concatenations_th:
    #    subject_level_concatenations_th[subj_name] = {
    #        'theta': [],
    #        'delta': [],
    #        'labels': []
    #    }
    
    #'''NEW'''
    if subj_name not in new_subject_level_concatenations_th:
        new_subject_level_concatenations_th[subj_name] = {
            'theta': [],
            'delta': [],
            'theta_strict': [],
            'labels': []
        }
        
    # Stampiamo le informazioni per ogni condizione
    print(f"\n\n\nSoggetto: \033[1m{subj_name}\033[0m, Condizione: \033[1m{condition}\033[0m")
    print(f"  - Theta shape: \033[1m{data['theta'].shape}\033[0m")
    print(f"  - Delta shape: \033[1m{data['delta'].shape}\033[0m")
    print(f"  - Theta Strict: \033[1m{data['coeff_fifth_detail_theta'].shape}\033[0m")
    print(f"  - Labels shape: \033[1m{len(data['labels'])}\033[0m")
    print(f"  - Valori unici delle etichette: \033[1m{np.unique(data['labels'])}\033[0m")
    
    
    #'''OLD'''
    # Concatenazione dei dati per i livelli theta, delta e labels
    #subject_level_concatenations_th[subj_name]['theta'].append(data['theta'])
    #subject_level_concatenations_th[subj_name]['delta'].append(data['delta'])
    #subject_level_concatenations_th[subj_name]['labels'].append(data['labels'])
    
    
    #'''NEW'''
    
    # Concatenazione dei dati per i livelli theta, delta e labels
    new_subject_level_concatenations_th[subj_name]['theta'].append(data['theta'])
    new_subject_level_concatenations_th[subj_name]['delta'].append(data['delta'])
    
    new_subject_level_concatenations_th[subj_name]['theta_strict'].append(data['coeff_fifth_detail_theta'])
    
    new_subject_level_concatenations_th[subj_name]['labels'].append(data['labels'])
    
    # Aggiorna il soggetto precedente
    previous_subject_suffix = subject_suffix

# Dopo aver iterato su tutte le condizioni, concatenare e stampare le informazioni dell'ultimo soggetto
if previous_subject_suffix is not None:
    
    last_subject_name = f'th_{previous_subject_suffix}'
    #levels = subject_level_concatenations_th[last_subject_name]
    levels = new_subject_level_concatenations_th[last_subject_name]
    
    print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('{last_subject_name}'):\033[0m\n")
    
    # Concatenazione dei dati dell'ultimo soggetto
    theta_concat = np.concatenate(levels['theta'], axis=0)
    delta_concat = np.concatenate(levels['delta'], axis=0)
    
    theta_concat_strict = np.concatenate(levels['theta_strict'], axis=0)
    
    labels_concat = np.concatenate(levels['labels'], axis=0)
    
    #'''OLD'''
    # Salvataggio dei dati concatenati dell'ultimo soggetto nel dizionario come array NumPy
    #subject_level_concatenations_th[last_subject_name] = {
    #    'theta': theta_concat,
    #    'delta': delta_concat,
    #    'labels': labels_concat
    #}
    
    #'''NEW'''
    # Salvataggio dei dati concatenati dell'ultimo soggetto nel dizionario come array NumPy
    new_subject_level_concatenations_th[last_subject_name] = {
       'theta': theta_concat,
        'delta': delta_concat,
        'theta_strict': theta_concat_strict,
        'labels': labels_concat
    }
    
    
    print(f"Soggetto: \033[1m{last_subject_name}\033[0m, "
          f"Theta shape: \033[1m{np.concatenate(levels['theta'], axis=0).shape}\033[0m, "
          f"Delta shape: \033{np.concatenate(levels['delta'], axis=0).shape}\033[0m, "
          f"Labels length: \033[1m{len(np.concatenate(levels['labels'], axis=0))}\033[0m\n\n")



In [ ]:
'''CHIAVI DI TUTTO IL DIZIONARIO '''
#subject_level_concatenations_th.keys()


new_subject_level_concatenations_th.keys()


#SOGGETTO 1

#CHIAVI
#subject_level_concatenations_th['th_1'].keys()

#DATI
#subject_level_concatenations_th['th_1']['theta'].shape

#new_subject_level_concatenations_th['th_1']['theta'].shape

#subject_level_concatenations_th['th_1']['delta'].shape

#LABELS
#subject_level_concatenations_th['th_1']['labels'].shape)
#type(subject_level_concatenations_th['th_1']['labels'])

# Check della concantenazione delle labels TH_1

#subject_level_concatenations_th['th_1']['labels'][:42]
#subject_level_concatenations_th['th_1']['labels'][41:81]
#subject_level_concatenations_th['th_1']['labels'][81:120]
#subject_level_concatenations_th['th_1']['labels'][121:164]

In [ ]:
#subject_level_concatenations_th['th_15']['labels'].shape

In [ ]:
#subject_level_concatenations_th['th_1'].keys()

#new_subject_level_concatenations_th['th_1'].keys()

print(np.unique(new_subject_level_concatenations_th['th_1']['labels'], return_counts = True))

In [ ]:
#unique_values, counts = np.unique(subject_level_concatenations_th['th_1']['labels'], return_counts=True)

#unique_values, counts = np.unique(new_subject_level_concatenations_th['th_1']['labels'], return_counts=True)

In [ ]:
#unique_values
#counts
#counts[0]

In [ ]:
!pwd

In [ ]:
#Salvo ricostruzioni 4° e 5° livello per singolo terapista con concatenazioni dati e labels 

    
''' PATH  --> cd Plots_Sliding_Estimator_MNE '''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('subject_level_concatenations_pt.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations_pt, f)
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_th, f)

### STEP 5.2.1 - All Therapists EEG Data Reconstructions across **Couples of Experimental Conditions**

#### Concatenazione All Single Subject Data (TH) per Coppie di Condizioni Sperimentali

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import pickle
import numpy as np

# Caricare l'intero dizionario annidato con pickle
with open('new_single_th_all_extracted_reconstructions.pkl', 'rb') as f:
    new_single_th_all_extracted_reconstructions = pickle.load(f)

In [ ]:
new_single_th_all_extracted_reconstructions.keys()

In [ ]:
new_single_th_all_extracted_reconstructions['wave_baseline_1'].keys()

#### Spiegazione STEP 5.2.1 - All Therapists EEG Data Reconstructions across Couples of Experimental Conditions

##### **Concatenazione All Single Subject Data (TH) per Coppie di Condizioni Sperimentali**

<br>

In questo caso, voglio **trasformare le variabili che contengono i miei dati e labels delle 4 condizioni sperimentali assieme**, in modo **da creare sottoinsiemi per ogni possibile coppia di condizioni sperimentali**. 

Dunque quello che si dovrà fare **per ogni coppia**:

1) **Filtrare i dati e le etichette**:

- **Estrarre** i dati associati **SOLO alle DUE condizioni in esame** (ad esempio 0 e 1, oppure 1 e 2).
- **Creare un nuovo array di etichette** e **un array di dati** ***corrispondenti*** **SOLO a quelle DUE condizioni**.

2) **Ripetere questa operazione per OGNI combinazione**:

- **Assicurarsi di considerare tutte le coppie** di condizioni sperimentali **SENZA ripetizioni** (ad esempio, non serve processare sia 0 vs 1 che 1 vs 0, perché sono equivalenti!).

3) **Creare quindi una struttura organizzata**, che contenga i dati e le etichette separatamente per ogni coppia, per ciascun livello di ricostruzione (theta, delta, theta_strict).

<br>

Quindi l'obiettivo è di modificare la procedura in modo da **concatenare SOLO le coppie di condizioni sperimentali per OGNI soggetto**. 

Per fare questo, possiamo utilizzare un **approccio combinatorio** per generare **tutte le possibili coppie di condizioni**.


Per quanto riguarda il calcolo combinatorio, possiamo usare il concetto di combinazioni per selezionare le coppie. 
Se hai 4 condizioni, il numero di combinazioni di coppie di condizioni (senza ripetizioni) si calcola come:

$$
\binom{4}{2} = \frac{4!}{2!(4-2)!} = 6
$$


Quindi, con 4 condizioni sperimentali, le combinazioni di coppie di condizioni saranno 6, e queste coppie sono:

(condizione 1, condizione 2) = 'baseline vs th_resp'
(condizione 1, condizione 3) = 'baseline vs pt_resp'
(condizione 1, condizione 4) = 'baseline vs shared_resp'
(condizione 2, condizione 3) = 'th_resp vs pt_resp'
(condizione 2, condizione 4) = 'th_resp vs shared_resp'
(condizione 3, condizione 4) = 'pt_resp vs shared_resp' 


<br>

Piano di modifiche al codice:

1) **Creazione delle coppie di condizioni**: Per ogni soggetto, genereremo tutte le coppie possibili di condizioni sperimentali. Utilizzeremo itertools.combinations per ottenere queste coppie.

2) **Concatenazione per ciascuna coppia**: Per ogni coppia di condizioni, concatenare i dati e le etichette delle due condizioni selezionate.

3) **Salvataggio delle concatenazioni**: Creeremo un dizionario per ciascuna coppia di condizioni per ogni soggetto.


**N.B.**

Nel codice che sto creando...

Ho fatto in modo che ci sia il modo di capire, **per ogni coppia di condizione sperimentale di dati e labels**, a quali condizione sperimentali di dati e labels ci si riferisca, mi spiego:

Sviluppo un **modo "standardizzato" per il quale per OGNI coppia di condizione sperimentale, la variabile che conterrà i dati e labels associate, sia chiamata in un certo modo**...

E nello specifico **con il nome delle DUE condizioni sperimentali che conterranno quei dati e relative labels**...

Del tipo: 

- se è baseline vs th_resp, la variabile sarà "baseline_vs_th_resp"
- se è baseline vs pt_resp, la variabile sarà "baseline_vs_pt_resp"
- se è baseline vs shared_resp, la variabile sarà "baseline_vs_shared_resp"


Senza contare che, questo **processo di standardizzazione del nome delle variabili**, deve esser fatto **per ogni livello di ricostruzione dei dati (sia 4° e 5° livello a partire dai coefficienti di approssimazione, che dal 5 ° livello dei coefficienti di dettaglio)**..

Questo significherebbe che, **per ogni soggetto**, dovrei (o potrei insomma) creare **un dizionario**, che 

- Contenga delle **sotto-chiavi di secondo ordine** (che son theta, delta e theta_strict) e dentro ognuna di queste
- Ci siano contenute **le relative 6 sotto-sotto-chiavi di terzo ordine**, relative ai dati e alle labels associate (anch'esse concatenate ovviamente) delle diverse combinazioni di condizioni sperimentali...


Ossia, vogliamo creare un dizionario strutturato che rappresenti ogni combinazione di coppie di condizioni sperimentali per ciascun soggetto, separando i dati e le etichette per i vari livelli di ricostruzione (theta, delta, theta_strict). 

Ogni combinazione di condizioni sperimentali sarà memorizzata in una chiave strutturata, come ad esempio "baseline_vs_th_resp", e all'interno di ciascuna chiave avremo le informazioni per i vari livelli di ricostruzione.


<br>


#### Esempio di Struttura proposta per il dizionario:


- Soggetto: ad esempio "th_1".
- Livelli di ricostruzione: theta, delta, theta_strict.
- Combinazioni di condizioni sperimentali: per ciascun livello di ricostruzione, avremo sotto-chiavi per ogni coppia di condizioni.

        new_subject_level_concatenations = {
            'th_1': {
                'theta': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                },
                'delta': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                },
                'theta_strict': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                }
            }
        }

<br>

**SOTTO-STEP 1: IDENTIFICAZIONE DELLE STRINGA NUMERICHE PER LA CREAZIONE DELLE VARIABILI - FUTURE CHIAVI - CHE CONTENGONO LE COPPIE DI DATI E LABELS DELLE RELATIVE COPPIE DI CONDIZIONI SPERIMENTALI CONSIDERATE NEL CICLO CORRENTE DEL LOOP**

Aspetta, ci sono altre cose che dovrebbero esser integrate nel codice...

cominciamo dalla prima, che è relativa all' "inferire" diciamo il nome da fornire alla variabile che conterrà i dati e labels delle due condizioni sperimentali correnti... e deve esser fatto, a partire dal nome delle chiavi di 

"new_single_th_all_extracted_reconstructions"...

ora, le sue chiavi son queste

dict_keys(['wave_baseline_1', 'wave_th_resp_1', 'wave_pt_resp_1', 'wave_shared_resp_1', 'wave_baseline_2', 'wave_th_resp_2', 'wave_pt_resp_2', 'wave_shared_resp_2', 'wave_baseline_3', 'wave_th_resp_3', 'wave_pt_resp_3', 'wave_shared_resp_3', 'wave_baseline_4', 'wave_th_resp_4', 'wave_pt_resp_4', 'wave_shared_resp_4', 'wave_baseline_5', 'wave_th_resp_5', 'wave_pt_resp_5', 'wave_shared_resp_5', 'wave_baseline_6', 'wave_th_resp_6', 'wave_pt_resp_6', 'wave_shared_resp_6', 'wave_baseline_7', 'wave_th_resp_7', 'wave_pt_resp_7', 'wave_shared_resp_7', 'wave_baseline_8', 'wave_th_resp_8', 'wave_pt_resp_8', 'wave_shared_resp_8', 'wave_baseline_9', 'wave_th_resp_9', 'wave_pt_resp_9', 'wave_shared_resp_9', 'wave_baseline_10', 'wave_th_resp_10', 'wave_pt_resp_10', 'wave_shared_resp_10', 'wave_baseline_11', 'wave_th_resp_11', 'wave_pt_resp_11', 'wave_shared_resp_11', 'wave_baseline_12', 'wave_th_resp_12', 'wave_pt_resp_12', 'wave_shared_resp_12'])


ora, il modo in cui si identifica un certo soggetto (ossia la chiavi di "primo ordine" che indentificano il soggetto, ossia ad esempio 'th_1'), dipenderebbe dal numero stringa che c'è alla fine di ogni nome stringa di ogni chiave dentro "new_single_th_all_extracted_reconstructions", mi spiego:

il codice dovrebbe capire che, ad esempio, solo l'ultima carattere stringa di queste prime 4 chiavi:

'wave_baseline_1', 'wave_th_resp_1', 'wave_pt_resp_1', 'wave_shared_resp_1', 

si riferisca al soggetto 1, ossia al futuro "th_1"...


per il soggetto 2, sarebbero: 

'wave_th_resp_2', 'wave_pt_resp_2', 'wave_shared_resp_2', e così via per gli altri soggetti..


Facendo attenzione al fatto che, dopo il soggetto 9, ovviamente, si passerà alle decine (a livello numerico), per cui saranno gli ultime due caratteri da considerare per l'identificazione delle sue rispettive chiavi, che in quel caso saranno per il soggetto 10, ossia il futuro th_10

'wave_baseline_10', 'wave_th_resp_10', 'wave_pt_resp_10', 'wave_shared_resp_10',

Inoltre, poi, per creare le variabili associate alle coppie di dati e labels delle relative condizioni sperimentali, dovrà il codice far in modo che il nome di quella variabile dipenda dalle stringhe sempre che si riferiscono al nome delle due chiavi di "new_single_th_all_extracted_reconstructions" da cui preleva i dati e le labels... 

ad esempio, se deve creare la variabile dei dati 'baseline_vs_th_resp" del primo soggetto, le chiavi rispettive da cui deve andare a prelevare le stringhe saranno appunto "'wave_baseline_1'" e "'wave_th_resp_1'"....

diciamo che si potrebbe creare una lista di stringhe che sarà del tipo:

experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp'], per vedere se una di queste sia dentro la rispettiva chiave di  new_single_th_all_extracted_reconstructions su cui sta iterando, che nel nostro caso di esempio sarebbero sempre

'wave_baseline_1' (e da cui vede che c'è la stinga 'baseline')
'wave_th_resp_1' (e da cui vede che c'è la stinga 'th_resp')

è chiaro?


<br>

In sostanza, desideri un modo per inferire dinamicamente il nome del soggetto e delle variabili che conterranno i dati e le etichette per ogni combinazione di condizioni, a partire dal nome delle chiavi di new_single_th_all_extracted_reconstructions. Ecco un piano per raggiungere questo obiettivo:

Passaggi:

- Identificare il soggetto:

Le chiavi di new_single_th_all_extracted_reconstructions finiscono con un numero che identifica il soggetto (es. wave_baseline_1, wave_th_resp_1, wave_pt_resp_1).
Questo numero può essere estratto dalle ultime cifre della chiave (ad esempio, 1 da wave_baseline_1).
La variabile associata a ciascun soggetto sarà chiamata th_X, dove X è il numero del soggetto.

- Generare dinamicamente il nome delle variabili:

A partire dai nomi delle chiavi, possiamo inferire quale combinazione di condizioni sperimentali stiamo trattando (es. baseline_vs_th_resp).
Creeremo una lista delle condizioni (experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']), quindi esamineremo le chiavi per determinare quali condizioni sono presenti.

- Creare il dizionario:

A ciascun soggetto verrà associato un dizionario, e per ogni combinazione di condizioni sperimentali, assoceremo i dati e le etichette in una chiave che seguirà la convenzione del tipo baseline_vs_th_resp.


<br>

Spiegazione:

1) Estrazione delle condizioni e soggetto:

La chiave, ad esempio wave_baseline_1, viene separata in parti. La parte baseline viene estratta per determinare la condizione, mentre 1 indica il numero del soggetto.
Queste informazioni vengono utilizzate per creare il nome del soggetto, th_1.

2) Combinazioni di condizioni:

La lista experimental_conditions contiene le 4 condizioni: baseline, th_resp, pt_resp, shared_resp.
Per ogni soggetto, controlliamo quali condizioni sono disponibili nella chiave (ad esempio, se il soggetto 1 ha wave_baseline_1 e wave_th_resp_1, creiamo la combinazione baseline_vs_th_resp).

3) Creazione dinamica delle variabili:

Utilizziamo la combinazione di condizioni per generare la chiave della variabile (baseline_vs_th_resp).
I dati e le etichette per la combinazione di condizioni vengono estratti e concatenati.


4) Risultato finale:

La struttura finale del dizionario new_subject_level_concatenations avrà una chiave per ciascun soggetto (th_1, th_2, ecc.), e sotto ogni soggetto ci saranno le combinazioni di condizioni per ciascun livello di ricostruzione (theta, delta, theta_strict), con i dati e le etichette corrispondenti.

<br>

Esempio di output:

    {
        'th_1': {
            'theta': {
                'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'th_resp_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                # Altre combinazioni...
            },
            'delta': {
                # Stessa struttura per 'delta'
            },
            'theta_strict': {
                # Stessa struttura per 'theta_strict'
            }
        }
    }

 
Questa struttura ti permetterà di avere un'organizzazione chiara e dinamica dei dati per ogni soggetto e combinazione di condizioni sperimentali.
 
 
<br>

**SOTTO-STEP 2: IDENTIFICAZIONE DELLE STRINGA ALFABETICHE PER LA CREAZIONE DELLE VARIABILI - FUTURE CHIAVI - CHE CONTENGONO IL NOME DELLE DUE COPPIE DI CONDIZIONI SPERIMENTALI DI CUI VENGONO PRELEVATI I DATI E LABELS CONCATENATI E CHE VENGONON CONSIDERATE NEL CICLO CORRENTE DEL LOOP**


ok, ora c'è una ultima cosa che mi manca da dirti, che è relativa alla ri-assegnazione del codice numerico associato ad ogni coppia di condizioni sperimentali...

nel senso che, originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò 

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo


print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n")
print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n")
print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n")
print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")


Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza,  nel tuo codice, ho bisogno che 

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre 

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e  e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare le labels andranno ovviamente riconvertite! Perché?
perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempip, in quel caso, le sue labels (che son  originariamente codificate come '1' in 'new_subject_level_concatenations'!) diveteranno '0', mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...


è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?


<br>

La **logica di ri-assegnazione delle etichette (labels)** è chiara e posso integrarla nel codice. 

La logica che stai descrivendo consiste essenzialmente nel **garantire che, quando crei una variabile che contiene dati e etichette per due condizioni sperimentali, le etichette siano sempre "0" per la prima condizione (cond_1) e "1" per la seconda condizione (cond_2)**, 

                **INDIPENDENTEMENTE** da come sono originariamente codificate in **"new_single_th_all_extracted_reconstructions"!
                
                

Ecco come possiamo procedere:

- Identificazione delle condizioni: Come hai descritto, determineremo le due condizioni sperimentali da confrontare, ad esempio "baseline" contro "th_resp", "baseline" contro "pt_resp", ecc.

- Riconversione delle etichette:

 - Se la condizione di confronto è "baseline" (che è associata a 0), non dobbiamo modificare le etichette.
 - Se la condizione di confronto non è "baseline", dovremo riconvertire le etichette di quella condizione a 0 e le etichette della condizione di confronto a 1.

- Struttura del codice: Durante la creazione delle variabili, dovremo controllare quale condizione è la prima (cond_1) e quale è la seconda (cond_2), e applicare questa logica per ri-assegnare le etichette di conseguenza.


<br>

Inoltre


dentro 

"# Crea tutte le combinazioni uniche di condizioni sperimentali (es. 'baseline vs th_resp')
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
"

Effettivamente vengono create delle tuple di coppie di stringhe che corrispondono a quelle con cui dovrebbero esser create le sotto-sotto-chiavi delle coppie di condizioni sperimentali..

tuttavia, è giusto che iteri rispetto a 'condition_pairs', ma deve inserire un qualche controllo anche rispetto a questa cosa:

originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo

print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n") print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n") print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n") print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")

Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza, nel tuo codice, ho bisogno che

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, che nel caso di "condition_pairs" dovrebbe corrispondere ai primi 3 elementi della sua lista no, perché sarebbero 

[('baseline', 'th_resp'), 
    ('baseline', 'pt_resp'), 
    ('baseline', 'shared_resp'), 

è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare, che fa riferimento a questi altri elementi di 
"condition_pairs" che è creato nel loop ossia

('th_resp', 'pt_resp'), 
('th_resp', 'shared_resp'), 
('pt_resp', 'shared_resp')]

le labels andranno ovviamente riconvertite! Perché? 

Perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempio, in quel caso, le sue labels (che son originariamente codificate come '1' in 'new_subject_level_concatenations'!) diventeranno '0',

mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...

è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?dentro "# Crea tutte le combinazioni uniche di condizioni sperimentali (es. 'baseline vs th_resp')
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
    "

effettivamente vengono create delle tuple di coppie di stringhe che corrispondono a quelle con cui dovrebbero esser create le sotto-sotto-chiavi delle coppie di condizioni sperimentali..

tuttavia, è giusto che iteri rispetto a 'condition_pairs', ma deve inserire un qualche controllo anche rispetto a questa cosa:

originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo

print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n") print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n") print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n") print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")

Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza, nel tuo codice, ho bisogno che

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, che nel caso di "condition_pairs" dovrebbe corrispondere ai primi 3 elementi della sua lista no, perché sarebbero 

[('baseline', 'th_resp'), 
    ('baseline', 'pt_resp'), 
    ('baseline', 'shared_resp'), 

è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare, che fa riferimento a questi altri elementi di 
"condition_pairs" che è creato nel loop ossia

('th_resp', 'pt_resp'), 
('th_resp', 'shared_resp'), 
('pt_resp', 'shared_resp')]

le labels andranno ovviamente riconvertite! Perché? 

Perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempio, in quel caso, le sue labels (che son originariamente codificate come '1' in 'new_subject_level_concatenations'!) diventeranno '0',

mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...

è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?



#### Implementazione STEP 5.2.1 - All Therapists EEG Data Reconstructions across Couples of Experimental Conditions

In [ ]:
new_single_th_all_extracted_reconstructions.keys()

In [ ]:
new_single_th_all_extracted_reconstructions['wave_baseline_1'].keys()

In [ ]:
type(new_single_th_all_extracted_reconstructions['wave_baseline_1']['theta'])

In [ ]:
print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n")
print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n")
print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n")
print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")

In [ ]:
new_single_th_all_extracted_reconstructions['wave_baseline_1'].keys()

In [ ]:
'''DETAILED VERSION WITH COMPLICATED PRINTS'''

import itertools
import numpy as np

experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']

# Nuova variabile per tracciare il soggetto corrente stampato
last_subject_key = None

# Dizionario per tenere traccia delle combinazioni già stampate per ogni soggetto
printed_combinations = {}

# Nuova variabile per memorizzare i risultati di dati e labels concatenati di coppie di condizioni sperimentali
new_subject_level_concatenations_coupled_exp_th = {}

# Loop su tutte le chiavi del dizionario iniziale
for key in new_single_th_all_extracted_reconstructions.keys():

    key_parts = key.split('_')
    subject_number = key_parts[-1] if key_parts[-1].isdigit() else None  # Verifica se è numerico
    
    # Verifica che il numero del soggetto sia valido
    if subject_number is None:
        continue  # Salta chiavi non valide
    
    subject_key = f"th_{subject_number}"  # Es. 'th_1' o 'th_12'
    
    '''PER TRACCIARE SOGGETTO PRECEDENTE'''
    # Aggiungi separazione visiva quando cambia il soggetto
    if subject_key != last_subject_key:
        if last_subject_key is not None:  # Evita di stampare separatori prima del primo soggetto
            print("\n" + "-" * 50 + f" END OF {last_subject_key.upper()} " + "-" * 50 + "\n")
        print(f"\nProcessing Subject: {subject_key}\n" + "=" * 80)
        
        # Inizializza il dizionario delle combinazioni stampate per il nuovo soggetto
        printed_combinations[subject_key] = set()  # Usando un set per evitare duplicati
    
    last_subject_key = subject_key  # Aggiorna il soggetto corrente
    
    # Inizializza la struttura se non esiste ancora
    if subject_key not in new_subject_level_concatenations_coupled_exp_th:
        new_subject_level_concatenations_coupled_exp_th[subject_key] = {'theta': {}, 'delta': {}, 'theta_strict': {}}
    
    # Crea tutte le combinazioni uniche di condizioni sperimentali (es. 'baseline vs th_resp')
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
    
    # Loop sulle combinazioni
    for cond_1, cond_2 in condition_pairs:
        
        # Crea il nome della variabile per la combinazione
        condition_pair_key = f"{cond_1}_vs_{cond_2}"
        
        # Controlla se la combinazione è già stata stampata per il soggetto corrente
        if condition_pair_key in printed_combinations[subject_key]:
            continue  # Salta la combinazione se è già stata stampata
        
        # Stampa il messaggio per la prima volta che incontriamo questa combinazione
        print(f"\n\t\tCreation of Coupled Condition \033[1m{condition_pair_key}\033[0m")
        
        # Aggiungi la combinazione al set delle combinazioni stampate per il soggetto
        printed_combinations[subject_key].add(condition_pair_key)
        
        # Ora esegui il ciclo sui livelli
        for level in ['theta', 'delta', 'coeff_fifth_detail_theta']:
            
            print(f"\n\t\t\t--- Level: \033[1m{level}\033[0m ---")
             
            # Gestisci il caso per 'coeff_fifth_detail_theta'
            if level == 'coeff_fifth_detail_theta':
                
                # Ottieni i dati e le etichette per il livello coeff_fifth_detail_theta
                data_cond_1 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_1}_{subject_number}", {}).get(level)
                print(f"Extracting data_cond_1 from {cond_1} which is ”wave_{cond_1}_{subject_number}\033[1m[{level}]\033[0m")
                
                labels_cond_1 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_1}_{subject_number}", {}).get('labels')
                print(f"Extracting labels_cond_1 from {cond_1} which is ”wave_{cond_1}_{subject_number}\033[1m[{level}]\033[0m['labels']")
                      
                data_cond_2 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_2}_{subject_number}", {}).get(level)
                print(f"Extracting data_cond_2 from {cond_2} which is ”wave_{cond_2}_{subject_number}\033[1m[{level}]\033[0m")
                
                labels_cond_2 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_2}_{subject_number}", {}).get('labels')
                print(f"Extracting labels_cond_2 from {cond_2} which is ”wave_{cond_2}_{subject_number}\033[1m[{level}]\033[0m['labels']\n")      
                    
            else:
                # Ottieni i dati e le etichette per gli altri livelli (theta, delta)
                data_cond_1 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_1}_{subject_number}", {}).get(level)
                print(f"Extracting data_cond_1 from {cond_1} which is ”wave_{cond_1}_{subject_number}\033[1m[{level}]\033[0m")
                
                labels_cond_1 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_1}_{subject_number}", {}).get('labels')
                print(f"Extracting labels_cond_1 from {cond_1} which is ”wave_{cond_1}_{subject_number}\033[1m[{level}]\033[0m['labels']")
                 
                data_cond_2 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_2}_{subject_number}", {}).get(level)
                print(f"Extracting data_cond_2 from {cond_2} which is ”wave_{cond_2}_{subject_number}\033[1m[{level}]\033[0m")
                
                labels_cond_2 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_2}_{subject_number}", {}).get('labels')
                print(f"Extracting labels_cond_2 from {cond_2} which is ”wave_{cond_2}_{subject_number}\033[1m[{level}]\033[0m['labels']\n")
                
            # Verifica che i dati siano validi
            if data_cond_1 is None or labels_cond_1 is None or data_cond_2 is None or labels_cond_2 is None:
                continue  # Salta combinazioni incomplete

            # Riassegna le etichette per garantire che "cond_1" = 0 e "cond_2" = 1
            labels_cond_1 = np.zeros_like(labels_cond_1, dtype=int)  # Tutte 0
            labels_cond_2 = np.ones_like(labels_cond_2, dtype=int)   # Tutte 1

            # Concatenazione dei dati e delle etichette
            concatenated_data = np.vstack((data_cond_1, data_cond_2))
            concatenated_labels = np.hstack((labels_cond_1, labels_cond_2))

            # Salva i risultati nella struttura
            if level == 'coeff_fifth_detail_theta':
                # Salva i dati sotto 'theta_strict' per 'coeff_fifth_detail_theta'
                new_subject_level_concatenations_coupled_exp_th[subject_key]['theta_strict'][condition_pair_key] = {
                    'data': concatenated_data,
                    'labels': concatenated_labels}
            else:
                # Salva i dati sotto i livelli 'theta' o 'delta'
                new_subject_level_concatenations_coupled_exp_th[subject_key][level][condition_pair_key] = {
                    'data': concatenated_data,
                    'labels': concatenated_labels}
    
        # Dopo aver trattato tutti i livelli, aggiungi una separazione visiva per il soggetto
        print("-" * 50 + f"-" * 50)

In [ ]:
print(f"\t\t\t\t\033[1mStructure of new_subject_level_concatenations_coupled_exp_th\033[0m: \n")
print(f"\033[1mFirst Order Keys\033[0m: {new_subject_level_concatenations_coupled_exp_th.keys()}\n")
print(f"\033[1mSecond Order Keys\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1'].keys()}\n")
print(f"\033[1mThird Order Keys\033[0m: \n{new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()}\n")
print(f"\033[1mFourth Order Keys\033[0m: \n{new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()}\n")

In [ ]:
'''VERIFICO CHE LA CONCATENAZIONE SIA AVVENUTA CORRETTAMENTE!'''

print("\tNOW, LET US SEE IF THE CONCATENATIONS RESPECT THE ORIGINAL SHAPES FOR EVERY COUPLED EXPERIMENTAL CONDITION!")
print("\tFOR THE 1°ST SUBJECT: CHECK IF THE SUM OF INDIVIDUAL EXP COND SHAPE MATCHES THE COUPLED COND CONCATENATION SHAPE:\n\n")

print("\033[1mINDIVIDUAL EXP COND SHAPE OF FIRST SUBJECT\033[0m:")


print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n")
print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n")
print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n")
print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")
print()

#new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['data'].shape

# Seleziona il primo soggetto (ad esempio, 'th_1')
subject_key = 'th_1'

# Itera per ogni livello e condizione sperimentale
for level in ['theta', 'delta', 'theta_strict']:
    print(f"\nShape of Coupled Experimental Data and Labels based on DWT Reconstructed Level \033[1m{level}\033[0m for subject \033[1m{subject_key}\033[0m\n")

    # Itera per ogni coppia di condizioni sperimentali
    for condition_pair_key, data_labels in new_subject_level_concatenations_coupled_exp_th[subject_key][level].items():
        
        # Estrai i dati e le etichette per ogni coppia di condizioni
        data = data_labels.get('data')
        labels = data_labels.get('labels')

        # Stampa il nome della coppia di condizioni e le loro dimensioni
        print(f"Condition Pair: \033[1m{condition_pair_key}\033[0m")
        
        if data is not None and labels is not None:
            print(f"  Data Shape: {data.shape}")
            print(f"  Labels Shape: {labels.shape}")
        else:
            print("  Missing data or labels!")

In [ ]:
print(np.unique(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['labels'], return_counts = True))
print(np.unique(new_subject_level_concatenations_coupled_exp_th['th_1']['theta_strict']['th_resp_vs_shared_resp']['labels'], return_counts = True))

In [ ]:
print(f"\t\t\t\033[1mBASELINE_VS_TH_RESP\033[0m\n")
print(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['labels'][:44])
print(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['labels'][45:])
print()
print()
print(f"\t\t\t\033[1mTH_RESP_VS_SHARED_RESP\033[0m\n")
print(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['th_resp_vs_shared_resp']['labels'][:40])
print(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['th_resp_vs_shared_resp']['labels'][41:])


#### STEP 5.2.1.2 - Salvataggio Dataset di All Single Therapists EEG Data Reconstructions across Couples of Experimental Conditions

In [ ]:
!pwd

In [ ]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE'''
import pickle

# Salvare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_coupled_exp_th, f)

### STEP 5.2.2 - Mi concateno le strutture dati e labels dei singoli Therapists EEG Data Reconstructions across **Couples of Experimental Conditions** INSIEME

#### Concatenazione All Single Subject Data (TH) per Coppie di Condizioni Sperimentali INSIEME

In [ ]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE'''

import pickle

path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{path}/new_subject_level_concatenations_coupled_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th = pickle.load(f)

In [ ]:
#new_subject_level_concatenations_coupled_exp_th.keys()
#new_subject_level_concatenations_coupled_exp_th['th_1'].keys()
#new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()
#new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()
#np.unique(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['labels'], return_counts = True)

In [ ]:
##NEW OFFICIAL VERSION!

#SENZA DICT_NAME!

import numpy as np

def concatenate_all_single_subj_wavelets_coupled_experimental_conditions_th(data_structure, wavelet_levels, conditions):
    
    """
    Concatena i dati e le etichette per ogni condizione sperimentale da una struttura dati con un livello in più,
    dove questo livello rappresenta le diverse coppie di condizioni sperimentali iterate nel ciclo ossia
    
    'baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 
    'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'
    
    ordinandoli anche per etichetta.
    
    Questo perché ogni array di labels avrà sempre o 0 od 1 come etichette,
    dato che son coppie di condizioni sperimentali

    Parameters:
        data_structure (dict): La struttura dati di input che contiene i dati per soggetti e condizioni.
        conditions (list): Le condizioni sperimentali (chiavi del secondo livello) da processare.
        

    Returns:
        dict: Un dizionario contenente i nuovi dizionari con 
        i dati concatenati e le etichette per ogni coppia di condizioni sperimentali
    
    """
        
        
    # Dizionario per contenere i dati concatenati di tutti i soggetti
    all_subj_data_by_coupled_cond = {}
    
    # Itera su ogni livello di ricostruzione wavelet ('theta', 'delta', 'theta_strict')
    
    for reconstruction_level in wavelet_levels:
        
        all_subj_data_by_coupled_cond[reconstruction_level] = {}  # Struttura annidata per livello

        # Itera su ogni coppia di condizioni sperimentali
        for condition_pair in conditions:
            
            #Dizionari per raccogliere dati e labels ordinati per ogni coppia di condizioni sperimentali
            # che è dinamico, per ogni coppia di condizioni sperimentali 
            #(quindi si ricreeranno passando alla condizione sperimentale successiva!)
            
            data_by_label = {}
            labels_by_label = {}
            shape_labels_per_subject = {0: [], 1: []}  # Inizializza il dizionario per 0 e 1

            # Itera su tutti i soggetti
            # In questo caso, itera sulle chiavi di ogni soggetto

            # Quindi prenderà, per la relativa coppia di condizioni sperimentali di ogni soggetto,
            # i dati e le labels di quel soggetto, per quella relativa coppia di condizioni sperimentali
            
            for subject_key in data_structure.keys():
                
                # Controlla se il livello di ricostruzione esiste per il soggetto
                if reconstruction_level not in data_structure[subject_key]:
                    continue
                    
                # Controlla se il livello di ricostruzione esiste per il soggetto
                if condition_pair not in data_structure[subject_key][reconstruction_level]:
                    continue
                
                # Qui estrae i dati e le labels per questa condizione sperimentale di quel soggettio lì
                subject_data = data_structure[subject_key][reconstruction_level][condition_pair]['data']
                subject_labels = data_structure[subject_key][reconstruction_level][condition_pair]['labels']
                
                # Trova le etichette uniche e gli indici corrispondenti per quella coppia di condizioni sperimentali lì,
                # Ossia, potrà trovare gli 0 e gli 1 
                
                unique_labels = np.unique(subject_labels)
                
                #A quel punto, per ognuna delle due labels trovate per quella coppia di condizioni sperimentali lì
                #Che saranno sempre o 0 o 1
                
                for label in unique_labels:
                    
                    # Trova gli indici dei dati corrispondenti a questa etichetta
                    # Una volta per lo 0 ed una volta per l' 1
                    
                    label_indices = np.where(subject_labels == label)[0]
                    
                    # A quel punto, estrae i dati e le labels per questi indici
                    # Una volta per lo 0 ed una volta per l' 1
                    
                    data_for_label = subject_data[label_indices]
                    labels_for_label = subject_labels[label_indices]
                    
                    # A quel punto, per ogni soggetto, per ogni condzione sperimentale, 
                    # per quelle due labels là (sempre presenti, per ogni coppia di condizioni sperimentali)
                    # Una volta per lo 0 ed una volta per l' 1

                    #Andrà a creare per ogni etichetta, una chiave che si chiamerà 
                    #o 0 od 1 (inizialmente, vuoto -> perché deve esser inizializzato)
                    #E poi, dopo, ci appenderà le labels 
                     # Una volta per lo 0 ed una volta per l' 1
                    #  Di quel soggetto per quella coppia di condizioni sperimentali iterate a quel momento
                    
                    #Aggiunge ai dizionari globali, creando la chiave se non esiste
                    if label not in data_by_label:
                        data_by_label[label] = []
                        labels_by_label[label] = []

                    data_by_label[label].append(data_for_label)
                    labels_by_label[label].append(labels_for_label)
                    
                    # **Salva la shape delle etichette per il soggetto corrente**
                    shape_labels_per_subject[label].append(labels_for_label.shape[0]) # Aggiungi solo la dimensione (numero di etichette)
                    
                    '''PRINT PER CHECK LABELS DI OGNI SOGGETTO PER OGNI COPPIA DI CONDIZIONE CONDIZIONI SPERIMENTALI''' 
                    #print(f"Soggetto: \033[1m{subject_key}\033[0m, Livello: \033[1m{reconstruction_level}\033[0m, Condizione: \033[1m{condition_pair}\033[0m, "
                    #      f"Etichetta: \033[1m{label}\033[0m, Shape: \033[1m{labels_for_label.shape[0]}\033[0m")
                    
                    # **Aggiungi un print di controllo per ogni soggetto**
                    #print(f"Soggetto: \033[1m{subject_key}\033[1m, Livello: {reconstruction_level}, Condizione: {condition_pair}, Etichetta: {label}, Shape: {labels_for_label.shape[0]}")
            
            
            #*** *** *** *** *** *** *** *** *** *** *** *** *** *** ***
            
            # Dopodiché, vado a creare invece i dizionari che conterranno
            # Le concatenazioni, di dati e labels corrispondenti, di tutti i soggetti per cui l'etichetta era 
            # o 0 od 1 

            # Di conseguenza, qui dentro dovrei avere, per ogni coppia di condizioni sperimentali
            # Tutti gli 0 ed 1 (ed i relativi dati corrispondenti)
            # di tutti i soggetti, ma concatenati

            concatenated_data_by_label = {}
            concatenated_labels_by_label = {}

            #for label in data_by_label.keys():
            #    if len(data_by_label[label]) > 0:  # Evita errori di concatenazione
            #        concatenated_data_by_label[label] = np.vstack(data_by_label[label])
            #        concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
            
            for label in data_by_label.keys():
                concatenated_data_by_label[label] = np.vstack(data_by_label[label])
                concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])

                # **Calcolare la shape totale delle etichette**
                #total_labels_0 = np.sum(1 for subject_labels in labels_by_label[label] if 0 in subject_labels)
                #total_labels_1 = np.sum(1 for subject_labels in labels_by_label[label] if 1 in subject_labels)
                #total_labels = total_labels_0 + total_labels_1

                # **Determinare gli indici delle etichette 0 e 1 nell'array finale**

                # Gli indici delle etichette 0
                indices_labels_0 = np.where(concatenated_labels_by_label[label] == 0)[0]

                # Gli indici delle etichette 1
                indices_labels_1 = np.where(concatenated_labels_by_label[label] == 1)[0]
                
                # Indici iniziale e finale per le etichette 0 e 1
                start_idx_0 = indices_labels_0[0] if len(indices_labels_0) > 0 else None
                end_idx_0 = indices_labels_0[-1] if len(indices_labels_0) > 0 else None
                start_idx_1 = indices_labels_1[0] if len(indices_labels_1) > 0 else None
                end_idx_1 = indices_labels_1[-1] if len(indices_labels_1) > 0 else None


                # **Print finale per verificare la concatenazione per ogni label**
                #print(f"\nCondizione: \033[1m{condition_pair}\033[0m, Etichetta: {label}")
                #print(f"  - Shape dei dati concatenati per \033[1m{label}\033[0m: {concatenated_data_by_label[label].shape}")
                #print(f"  - Shape delle etichette concatenate per \033[1m{label}\033[0m: {concatenated_labels_by_label[label].shape}")

                # **Stampa la lista delle shapes delle etichette per ogni soggetto per questa etichetta**
                #print(f"\n  - Shape delle etichette per soggetto (per etichetta {label}): {shape_labels_per_subject[label]}\n")


                # **Stampa il conteggio totale delle etichette**
                #print(f"\n  - Totale delle etichette 0: {total_labels_0}")
                #print(f"  - Totale delle etichette 1: {total_labels_1}")
                #print(f"  - Totale delle etichette per la condizione: {total_labels}\n")

                # **Stampa gli indici per le etichette 0 e 1**
                # **OSSIA --> Stampa gli indici per l'etichetta corrente**

                #if label == 0:
                #    print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
                #else:
                #    print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}\n")


                #print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
                #print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}")


            #ARRIVATI FINO A QUI, abbiamo che siccome stiamo iterando prima per tutti gli 0 e poi per tutti gli 1
            #Significa che, assumendo che siamo dentro 'baseline_vs_th_resp' e che 

            #'baseline' sia rappresentato dalle etichette 0
            #'th_resp' sia rappresentato dalle etichette 1

            #Al PRIMO ciclo avrò che:

            #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti)
            #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'baseline' per 'baseline_vs_th_resp'di tutti i soggetti)

            #Al SECONDO ciclo avrò che:

            #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
            #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)

            #Quindi mi manca ancora 

            #A) CONCATENARE I DATI:

            #1)prima tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 

            #CON

            #2)tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)

            #che verrà fatto dentro all_data (che è anch'esso una variabile dinamica!)

            #B) CONCATENARE LE LABELS:

            #1)prima tutti le labels (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 

            #CON

            #2)tutte le labels (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)

            #che verrà fatto dentro all_labels (che è anch'esso una variabile dinamica!)

            # Liste per raccogliere dati e labels di tutte le etichette

            # Qui dentro, invece, dov con
            
            all_data = []
            all_labels = []

            for label in concatenated_data_by_label.keys():
                all_data.append(concatenated_data_by_label[label])
                all_labels.append(concatenated_labels_by_label[label])
            
            #Alla fine, qui dentro avrò che, PER OGNI COPPIA DI CONDIZIONI SPERIMENTALI


            #'final_data' dovrebbe avere 
                #- prima tutti i dati di tutti i soggetti associati all'etichetta 0 
                #- e poi tutti i dati di tutti i soggetti associati all'etichetta 1

            #'final_labels' dovrebbe avere 
                #- prima tutte le labels di tutti i soggetti associati all'etichetta 0
                #- e poi tutte tutte le labels di tutti soggetti associati all'etichetta 1...
                
            if all_data:  # Evita errori di concatenazione se non ci sono dati
                final_data = np.vstack(all_data)
                final_labels = np.hstack(all_labels)
                
                all_subj_data_by_coupled_cond[reconstruction_level][condition_pair] = {
                    'data': final_data,
                    'labels': final_labels
                }
                

    #print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")

    #for reconstruction_level, conditions_dict in all_subj_data_by_coupled_cond.items():
    #    for condition_pair, value in conditions_dict.items():
    #        labels = value['labels']
    #        unique_labels = np.unique(labels)
    #        total_labels = 0

    #        print(f"\nLivello Wavelet: {reconstruction_level}, Condizione: {condition_pair}")
    #        for label in unique_labels:
    #            label_indices = np.where(labels == label)[0]
    #            start_idx = label_indices[0] if len(label_indices) > 0 else None
    #            end_idx = label_indices[-1] if len(label_indices) > 0 else None
    #            total_labels += len(label_indices)

    #            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m "
    #                  f"(Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

    #        print(f"Totale etichette (0 e 1): \033[1m{total_labels}\033[0m\n")

    return all_subj_data_by_coupled_cond


In [ ]:
# Parametri
conditions = ['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp',
              'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp']


wavelet_levels = ['theta', 'delta', 'theta_strict']

# Chiamata alla funzione, qui definisco a mano il nome della variabile (i.e., 
new_all_th_concat_reconstructions_wavelet_levels_coupled_exp = concatenate_all_single_subj_wavelets_coupled_experimental_conditions_th(
    data_structure=new_subject_level_concatenations_coupled_exp_th,
    wavelet_levels = wavelet_levels,
    conditions=conditions
)

print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")

for reconstruction_level, conditions_dict in new_all_th_concat_reconstructions_wavelet_levels_coupled_exp.items():
    for condition_pair, value in conditions_dict.items():
        labels = value['labels']
        unique_labels = np.unique(labels)
        total_labels = 0

        print(f"\nLivello Wavelet: \033[1m{reconstruction_level}\033[0m, Condizione: \033[1m{condition_pair}\033[0m")
        for label in unique_labels:
            label_indices = np.where(labels == label)[0]
            start_idx = label_indices[0] if len(label_indices) > 0 else None
            end_idx = label_indices[-1] if len(label_indices) > 0 else None
            total_labels += len(label_indices)

            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m "
                  f"(Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

        print(f"Totale etichette (0 e 1): \033[1m{total_labels}\033[0m\n")

In [ ]:
#new_concatenated_dictionaries.keys()
#new_concatenated_dictionaries['theta'].keys()
#new_concatenated_dictionaries['theta']['baseline_vs_th_resp'].keys()
#np.unique(new_concatenated_dictionaries['theta']['baseline_vs_th_resp']['labels'], return_counts = True)

#### STEP 5.2.2.1 - Salvataggio Dataset di **All Single Therapists** EEG Data Reconstructions across **Couples of Experimental Conditions** INSIEME

In [ ]:
pwd

In [ ]:
cd ..

In [ ]:
cd all_datas/

In [ ]:
''' PATH  --> cd Unfamiliar_Wavelet_Reconstructions '''
import pickle
import os
   
base_path = '/home/stefano/Interrogait/all_datas/Familiar_Wavelet_Reconstructions'

# Controlla se la cartella esiste, altrimenti la crea
if not os.path.exists(base_path):
    os.makedirs(base_path)
    
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_wavelet_levels_coupled_exp.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_wavelet_levels_coupled_exp, f)

### STEP 5.3 - All Patients EEG Data Reconstructions

#### Concatenazione All Single Subject Data (PT) per tutte le condizioni sperimentali, per ogni livello di ricostruzione (θ and δ)

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''

#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('all_subjects_condition_results_pt.pkl', 'rb') as f:
#    all_subjects_condition_results_pt = pickle.load(f)
    
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_all_subjects_condition_results_pt.pkl', 'rb') as f:
    new_all_subjects_condition_results_pt = pickle.load(f)

In [ ]:
#print(f"\033[1mChiavi di primo ordine\033[0m i.e., all_subjects_condition_results_pt: \n\n{all_subjects_condition_results_py.keys()}")
#print(f"\n\n\033[1mChiavi di ogni condizione sperimentale\033[0m, i.e., 'wave_baseline_1': {all_subjects_condition_results_pt['wave_baseline_1'].keys()}")

#all_subjects_condition_results_pt['wave_baseline_1'].keys()


print(f"\033[1mChiavi di primo ordine\033[0m i.e., new_all_subjects_condition_results_pt: \n\n{new_all_subjects_condition_results_pt.keys()}")
print(f"\n\n\033[1mChiavi di ogni condizione sperimentale\033[0m, i.e., 'wave_baseline_1': {new_all_subjects_condition_results_pt['wave_baseline_1'].keys()}")


In [ ]:
#new_all_subjects_condition_results_th['wave_baseline_1'].keys()
print(new_all_subjects_condition_results_pt['wave_baseline_1']['A'].shape)
print(new_all_subjects_condition_results_pt['wave_baseline_1']['D'].shape)

In [ ]:
'''
Da "all_subjects_condition_results" ottengo:

Le ricostruzioni 4° e 5° livello di tutti i terapisti per tutte le condizioni sperimentali dai coefficienti di approssimazione
Le ricostruzioni 5° livello di tutti i terapisti per tutte le condizioni sperimentali dai coefficienti di dettaglio

				(i.e., single_pt_all_extracted_reconstructions):

'''

import numpy as np

# Definizione degli indici dei canali desiderati
selected_channels = [12, 30, 48]  # Indici per Fz, Cz, Pz

# Creazione di un dizionario dei dati di tutti i terapisti singolarmente, per salvare le ricostruzioni estratte per livello 4 e 5
#single_pt_all_extracted_reconstructions = {}

new_single_pt_all_extracted_reconstructions = {}

# Iterazione su tutte le condizioni sperimentali di tutti i soggetti 

#'OLD VERSION'
#for condition, data in all_subjects_condition_results_pt.items():

for condition, data in new_all_subjects_condition_results_pt.items():
    
    # Estrarre le etichette per questa condizione
    A_labels = data['A_labels']
    
    # Estrazione della matrice 'A' per le ricostruzioni del segnale con coefficienti di approssimazione
    A = data['A']
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Estrazione della matrice 'D' per le ricostruzioni del segnale con coefficienti di approssimazione
    D = data['D']
    
    # Estrarre solo i canali selezionati e i livelli di ricostruzione desiderati (4° e 5°, quindi indice -2 e -1)
    theta_reconstruction = A[:, selected_channels, :, -2]  # 4° livello di ricostruzione
    delta_reconstruction = A[:, selected_channels, :, -1]  # 5° livello di ricostruzione
    
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Ottenere i coefficienti di dettaglio del 5° livello di ricostruzione (theta range)
    coeff_fifth_detail_theta = D[:, selected_channels, :, -1]  # Coefficienti di dettaglio del livello 5
    
    
    # Trasponi per ottenere la forma desiderata: (trials, canali, punti temporali)
    theta_reconstruction = theta_reconstruction.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    delta_reconstruction = delta_reconstruction.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    coeff_fifth_detail_theta = coeff_fifth_detail_theta.transpose(1, 0, 2)  # Da (3, 42, 300) a (42, 3, 300)
    
    #'''AGGIUNTA PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    # Creare un sotto-dizionario per organizzare 
    #le ricostruzioni EEG del livello 4 'theta' e livello 5 'delta' dai coeff di approx
    #le ricostruzioni EEG del livello 4 'theta' e livello 5 'delta' dai coeff di detail
    
    new_single_pt_all_extracted_reconstructions[condition] = {
        'theta': theta_reconstruction,
        'delta': delta_reconstruction,
        'coeff_fifth_detail_theta': coeff_fifth_detail_theta, 
        'labels': A_labels
    }

# Verifica delle dimensioni del risultato estratto per una condizione specifica
print(f"\t\t\033[1mRicostruzioni 4° e 5° livello di tutti i pazienti per tutte le condizioni sperimentali")
#print(f"\n\n\t\t\t\t(i.e., \033[1msingle_pt_all_extracted_reconstructions\033[0m):\n")

print(f"\n\n\t\t\t\t(i.e., \033[1mnew_single_pt_all_extracted_reconstructions\033[0m):\n")


#for condition, extracted_data in single_pt_all_extracted_reconstructions.items():

#'''AGGIUNTI COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''

for condition, extracted_data in new_single_pt_all_extracted_reconstructions.items():
    
    print(f"Condizione: \033[1m{condition}\033[0m, "
          f"Theta shape: \033[1m{extracted_data['theta'].shape}\033[0m, "
          f"Delta shape: \033[1m{extracted_data['delta'].shape}\033[0m, "
          f"Coeff Fifth Detail shape: \033[1m{extracted_data['coeff_fifth_detail_theta'].shape}\033[0m, "
          f"Labels: \033[1m{len(extracted_data['labels'])}\033[0m")

# STEP 2: Concatenare i dati e le etichette di tutti i soggetti per i livelli di ricostruzione 4 e 5

# Inizializzazione delle liste per raccogliere i dati e le etichette del 4° e 5° livello di ricostruzione da coeff approx

all_pt_fourth = []
labels_pt_fourth = []
exp_conditions_fourth = []

all_pt_fifth = []
labels_pt_fifth = []
exp_conditions_fifth = []


#'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''

all_pt_fifth_detail = []
labels_pt_fifth_detail = []
exp_conditions_fifth_detail = []

# Iterazione su tutte le condizioni sperimentali

#for condition, data in single_pt_all_extracted_reconstructions.items():
for condition, data in new_single_pt_all_extracted_reconstructions.items():    
    
    # Preparazione delle liste per dati e etichette per ogni condizione
    dati_fourth = [None] * 4  # Per 'baseline', 'th_resp', 'vision_resp', 'shared_resp'
    labels_fourth = [None] * 4
    
    dati_fifth = [None] * 4
    labels_fifth = [None] * 4
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    dati_fifth_detail = [None] * 4
    labels_fifth_detail = [None] * 4
    
    for chiave, valore in data.items():
        
        if chiave == 'theta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            if 'baseline' in condition:
                dati_fourth[0] = valore
                labels_fourth[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fourth[1] = valore
                labels_fourth[1] = data['labels']
            
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fourth[2] = valore
                labels_fourth[2] = data['labels']
                
            elif 'shared_resp' in condition:
                dati_fourth[3] = valore
                labels_fourth[3] = data['labels']
                
        elif chiave == 'delta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            if 'baseline' in condition:
                dati_fifth[0] = valore
                labels_fifth[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fifth[1] = valore
                labels_fifth[1] = data['labels']
            
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fifth[2] = valore
                labels_fifth[2] = data['labels']
                
                
            elif 'shared_resp' in condition:
                dati_fifth[3] = valore
                labels_fifth[3] = data['labels']
        
        elif chiave == 'coeff_fifth_detail_theta':
            
            # Estrarre il tipo di risposta dalla chiave della condizione
            
            if 'baseline' in condition:
                dati_fifth_detail[0] = valore
                labels_fifth_detail[0] = data['labels']
                
            elif 'th_resp' in condition:
                dati_fifth_detail[1] = valore
                labels_fifth_detail[1] = data['labels']
                
            #'''OLD VERSION'''
            #elif 'vision_resp' in condition:
            #    dati_fourth[2] = valore
            #    labels_fourth[2] = data['labels']
            
            #'''NEW VERSION'''
            elif 'pt_resp' in condition:
                dati_fifth_detail[2] = valore
                labels_fifth_detail[2] = data['labels']
                
            elif 'shared_resp' in condition:
                dati_fifth_detail[3] = valore
                labels_fifth_detail[3] = data['labels']
                
            
    # Filtrare i valori non None
    dati_fourth = [d for d in dati_fourth if d is not None]
    labels_fourth = [l for l in labels_fourth if l is not None]
    
    dati_fifth = [d for d in dati_fifth if d is not None]
    labels_fifth = [l for l in labels_fifth if l is not None]
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    dati_fifth_detail = [d for d in dati_fifth_detail if d is not None]
    labels_fifth_detail = [l for l in labels_fifth_detail if l is not None]
    
    # Concatenare i dati e le etichette
    if dati_fourth:
        datas_fourth = np.concatenate(dati_fourth, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fourth = np.concatenate([np.array(l) for l in labels_fourth], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_pt_fourth.append(datas_fourth)
        labels_pt_fourth.append(labels_fourth)
        exp_conditions_fourth.append(condition)
    
    if dati_fifth:
        datas_fifth = np.concatenate(dati_fifth, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fifth = np.concatenate([np.array(l) for l in labels_fifth], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_pt_fifth.append(datas_fifth)
        labels_pt_fifth.append(labels_fifth)
        exp_conditions_fifth.append(condition)
    
    
    #'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
    if dati_fifth_detail:
        
        datas_fifth_detail = np.concatenate(dati_fifth_detail, axis=0)  # Concatenazione lungo la dimensione dei trials
        labels_fifth_detail = np.concatenate([np.array(l) for l in labels_fifth_detail], axis=0)  # Concatenazione lungo la dimensione dei trials
        
        all_pt_fifth_detail.append(datas_fifth_detail)
        labels_pt_fifth_detail.append(labels_fifth_detail)
        exp_conditions_fifth_detail.append(condition)

# STEP 3: Concatenazione finale di tutti i dati e le etichette

# Concatenazione finale di tutti i dati e le etichette

#'''PER COEFFICIENTI DI APPROSSIMAZIONE 4° LIVELLO (i.e., range 0-7.812Hz)'''
if all_pt_fourth:
    all_fourth = np.concatenate(all_pt_fourth, axis=0)
else:
    all_fourth = np.array([])

if labels_pt_fourth:
    all_fourth_labels = np.concatenate(labels_pt_fourth, axis=0)
else:
    all_fourth_labels = np.array([])

    
#'''PER COEFFICIENTI DI APPROSSIMAZIONE 5° LIVELLO (i.e., range 0-3.9Hz)'''    
if all_pt_fifth:
    all_fifth = np.concatenate(all_pt_fifth, axis=0)
else:
    all_fifth = np.array([])

if labels_pt_fifth:
    all_fifth_labels = np.concatenate(labels_pt_fifth, axis=0)
else:
    all_fifth_labels = np.array([])
    

#'''PER COEFFICIENTI DI DETTAGLIO 5° LIVELLO (i.e., range 3.9-7.812Hz)'''
if all_pt_fifth_detail:
    all_fifth_detail = np.concatenate(all_pt_fifth_detail, axis=0)
else:
    all_fifth_detail = np.array([])

if labels_pt_fifth_detail:
    all_fifth_detail_labels = np.concatenate(labels_pt_fifth_detail, axis=0)
else:
    all_fifth_detail_labels = np.array([])
    

# Verifica delle dimensioni del risultato finale
print(f"\n\n\n\t\tTUTTI I TRIAL DI TUTTI I SOGGETTI DI OGNI CONDIZIONE SPERIMENTALE - PER LIVELLO DI RICOSTRUZIONE ")

print(f"\n\033[1m4° livello\033[0m di ricostruzione da Coeff di Approx - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fourth\033[0m: \033[1m{all_fourth.shape}\033[0m, Length di \033[1mall_fourth_labels\033[0m: \033[1m{len(all_fourth_labels)}\033[0m")

print(f"\n\033[1m5° livello\033[0m di ricostruzione da Coeff di Approx - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fifth\033[0m: \033[1m{all_fifth.shape}\033[0m, Length di \033[1mall_fifth_labels\033[0m: \033[1m{len(all_fifth_labels)}\033[0m")

print(f"\n\033[1m5° livello\033[0m di ricostruzione da Coeff di Detail - Tutte le Condizioni Sperimentali:")
print(f"Shape di \033[1mall_fifth_detail\033[0m: \033[1m{all_fifth_detail.shape}\033[0m, Length di \033[1mall_fifth_detail_labels\033[0m: \033[1m{len(all_fifth_detail_labels)}\033[0m")


In [ ]:
!pwd

In [ ]:
#Salvo ricostruzioni 4° e 5° livello per singolo terapista con concatenazioni dati e labels 

''' PATH  --> cd Plots_Sliding_Estimator_MNE '''

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('single_pt_all_extracted_reconstructions.pkl', 'wb') as f:
#    pickle.dump(single_pt_all_extracted_reconstructions, f)
    
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''
import pickle

# Salvare l'intero dizionario annidato con pickle
with open('new_single_pt_all_extracted_reconstructions.pkl', 'wb') as f:
    pickle.dump(new_single_pt_all_extracted_reconstructions, f)   

In [ ]:
'''SALVO IN UN GRANDE DIZIONARIO I DATI E LE LABELS CONCATENATI DI TUTTI I SOGGETTI PER IL LIVELLO DI RICOSTRUZIONE'''


#Creo dizionario per le concatenazioni di dati e labels a seconda del livello di ricostruzione del segnale EEG 
new_all_pt_concat_reconstructions = {'all_pt_fourth': all_fourth, 
                                 'all_pt_fourth_labels': all_fourth_labels,
                                 'all_pt_fifth': all_fifth,
                                 'all_pt_fifth_labels': all_fifth_labels,
                                 'all_pt_fifth_detail': all_fifth_detail,
                                 'all_pt_fifth_detail_labels': all_fifth_detail_labels}


'''STAMPA DELLE CHIAVI e SHAPE'''
#all_pt_concat_reconstructions.keys()
#all_pt_concat_reconstructions['all_pt_fourth'].shape
#all_pt_concat_reconstructions['all_pt_fourth_labels'].shape

#all_pt_concat_reconstructions['all_pt_fifth'].shape
#all_pt_concat_reconstructions['all_pt_fifth_labels'].shape



#all_pt_concat_theta = {'all_pt_fourth': all_fourth, 
#                       'all_pt_fourth_labels': all_fourth_labels}


#all_pt_concat_delta = {'all_pt_fifth': all_fifth,
#                       'all_pt_fifth_labels': all_fifth_labels}


#all_pt_concat_theta.keys()
#all_pt_concat_delta.keys()

In [ ]:
new_all_pt_concat_reconstructions.keys()

In [ ]:
'''SALVO I DATI CONCATENATI DI TUTTI I SOGGETTI TERAPISTI, RISPETTO AD UNO SPECIFICO LIVELLO DI RICOSTRUZIONE'''

import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_fourth_pt.pkl', 'wb') as f:
    pickle.dump(all_fourth, f) 


import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_fifth_pt.pkl', 'wb') as f:
    pickle.dump(all_fifth, f) 

    
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_fifth_detail_pt.pkl', 'wb') as f:
    pickle.dump(all_fifth_detail, f) 

'''SALVO I DATI CONCATENATI DI TUTTI I SOGGETTI TERAPISTI, RISPETTO AD OGNI LIVELLO DI RICOSTRUZIONE INSIEME'''
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_all_pt_concat_reconstructions.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions, f)   

In [ ]:
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_single_pt_all_extracted_reconstructions.pkl', 'rb') as f:
    new_single_pt_all_extracted_reconstructions = pickle.load(f)

In [ ]:
#Dizionario con dati e labels 
#a seconda del livello di ricostruzione del segnale EEG 
#di ogni singolo soggetto 
#per tutte le condizioni sperimentali SEPARATAMENTE!

'''OLD'''
#print(f"\n\033[1msingle_pt_all_extracted_reconstructions.keys()\033[0m: \n{single_pt_all_extracted_reconstructions.keys()}\n")
#print(f"\n\033[1msingle_pt_all_extracted_reconstructions['wave_baseline_1'].keys()\033[0m: {single_pt_all_extracted_reconstructions['wave_baseline_1'].keys()}")


'''NEW'''
print(f"\n\033[1mnew_single_pt_all_extracted_reconstructions.keys()\033[0m: \n{new_single_pt_all_extracted_reconstructions.keys()}\n")
print(f"\n\033[1mnew_single_pt_all_extracted_reconstructions['wave_baseline_1'].keys()\033[0m: {new_single_pt_all_extracted_reconstructions['wave_baseline_1'].keys()}")


#single_pt_all_extracted_reconstructions['wave_baseline_1']['theta'].shape
#single_pt_all_extracted_reconstructions['wave_baseline_1']['delta'].shape
#len(single_pt_all_extracted_reconstructions['wave_baseline_1']['labels'])

In [ ]:
# Itera su ogni chiave nel dizionario new_single_th_all_extracted_reconstructions
for main_key in new_single_pt_all_extracted_reconstructions.keys():
    
    # Verifica se 'coeff_fifth_detail_theta' è presente tra le sottochiavi
    if 'coeff_fifth_detail_theta' not in new_single_pt_all_extracted_reconstructions[main_key]:
        print(f"La chiave '{main_key}' \033[1mNON contiene\033[0m 'coeff_fifth_detail_theta'")
    else:
        print(f"La chiave '{main_key}' contiene 'coeff_fifth_detail_theta'")


In [ ]:
'''
Questa struttura consente di avere i dati correttamente organizzati e concatenati per ogni soggetto 
in base al livello di ricostruzione, 
mantenendo la corrispondenza tra dati e etichette per ogni condizione sperimentale

Da           "single_pt_all_extracted_reconstructions"       a            "subject_level_concatenations_pt"

Da           "new_single_pt_all_extracted_reconstructions"       a       "new_subject_level_concatenations_pt"
'''

import numpy as np

# Dizionario per contenere i dati concatenati per ogni soggetto e livello di ricostruzione
new_subject_level_concatenations_pt = {}

# Variabile per tracciare il soggetto precedente
previous_subject_suffix = None

print(f"\t\t\033[1mConcatenazione dati 4° e 5° livello di OGNI paziente di TUTTE le condizioni sperimentali INSIEME\033[0m")
#print(f"\n\t\tda\t\033[1m'single_pt_all_extracted_reconstructions'\033[0m \ta\t\033[1m'subject_level_concatenations_pt'\033[0m")

print(f"\n\t\tda\t\033[1m'new_single_pt_all_extracted_reconstructions'\033[0m \ta\t\033[1m'new_subject_level_concatenations_pt'\033[0m")

# Iterazione su tutte le chiavi di single_pt_all_extracted_reconstructions

#'''OLD VERSION'''
#for condition, data in single_pt_all_extracted_reconstructions.items():

for condition, data in new_single_pt_all_extracted_reconstructions.items():
    
    # Estrazione del suffisso numerico del soggetto (es. '1', '2', ...)
    subject_suffix = condition.split('_')[-1]  # Prende solo la parte numerica
    
    # Creazione del nome della chiave del soggetto specifico
    subj_name = f'pt_{subject_suffix}'  # Crea la chiave con prefisso 'pt_' e suffisso numerico
    
    # Se stiamo per passare a un nuovo soggetto, stampiamo le dimensioni delle concatenazioni per il soggetto precedente
    if previous_subject_suffix is not None and subject_suffix != previous_subject_suffix:
        
        print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('pt_{previous_subject_suffix}'):\033[0m\n")
        prev_subject_name = f'pt_{previous_subject_suffix}'
        
        #levels = subject_level_concatenations_pt[prev_subject_name]
        
        levels = new_subject_level_concatenations_pt[prev_subject_name]
        
        # Concatenazione dei dati prima della stampa
        theta_concat = np.concatenate(levels['theta'], axis=0)
        delta_concat = np.concatenate(levels['delta'], axis=0)
        
        #Coefficienti di dettaglio 5° livello theta
        theta_concat_strict = np.concatenate(levels['theta_strict'], axis=0)
        
        labels_concat = np.concatenate(levels['labels'], axis=0)
        
        #if 'coeff_fifth_detail_theta' not in levels:
        #    print(f"La chiave 'coeff_fifth_detail_theta' non è presente per il soggetto: {prev_subject_name}")

        print(f"Soggetto: \033[1m{prev_subject_name}\033[0m, "
              f"Theta shape: \033[1m{np.concatenate(levels['theta'], axis=0).shape}\033[0m, "
              f"Delta shape: \033[1m{np.concatenate(levels['delta'], axis=0).shape}\033[0m, "
              f"Theta Strict shape: \033[1m{np.concatenate(levels['theta_strict'], axis=0).shape}\033[0m, "
              f"Labels length: \033[1m{len(np.concatenate(levels['labels'], axis=0))}\033[0m")
        
        
        #'''OLD'''
        # Salvataggio dei dati concatenati nel dizionario come array NumPy
        #subject_level_concatenations_pt[prev_subject_name]['theta'] = theta_concat
        #subject_level_concatenations_pt[prev_subject_name]['delta'] = delta_concat
        #subject_level_concatenations_pt[prev_subject_name]['labels'] = labels_concat
        
        
        #'''NEW'''
        new_subject_level_concatenations_pt[prev_subject_name]['theta'] = theta_concat
        new_subject_level_concatenations_pt[prev_subject_name]['delta'] = delta_concat
        
        new_subject_level_concatenations_pt[prev_subject_name]['theta_strict'] = theta_concat_strict
        
        new_subject_level_concatenations_pt[prev_subject_name]['labels'] = labels_concat
    
    #'''OLD'''
    # Inizializzare il dizionario per il soggetto specifico se non esiste già
    #if subj_name not in subject_level_concatenations_pt:
    #    subject_level_concatenations_pt[subj_name] = {
    #        'theta': [],
    #        'delta': [],
    #        'labels': []
    #    }
    
    #'''NEW'''
    if subj_name not in new_subject_level_concatenations_pt:
        new_subject_level_concatenations_pt[subj_name] = {
            'theta': [],
            'delta': [],
            'theta_strict': [],
            'labels': []
        }
        
    # Stampiamo le informazioni per ogni condizione
    print(f"\n\n\nSoggetto: \033[1m{subj_name}\033[0m, Condizione: \033[1m{condition}\033[0m")
    print(f"  - Theta shape: \033[1m{data['theta'].shape}\033[0m")
    print(f"  - Delta shape: \033[1m{data['delta'].shape}\033[0m")
    print(f"  - Theta Strict: \033[1m{data['coeff_fifth_detail_theta'].shape}\033[0m")
    print(f"  - Labels shape: \033[1m{len(data['labels'])}\033[0m")
    print(f"  - Valori unici delle etichette: \033[1m{np.unique(data['labels'])}\033[0m")
    
    
    #'''OLD'''
    # Concatenazione dei dati per i livelli theta, delta e labels
    #subject_level_concatenations_pt[subj_name]['theta'].append(data['theta'])
    #subject_level_concatenations_pt[subj_name]['delta'].append(data['delta'])
    #subject_level_concatenations_pt[subj_name]['labels'].append(data['labels'])
    
    
    #'''NEW'''
    
    # Concatenazione dei dati per i livelli theta, delta e labels
    new_subject_level_concatenations_pt[subj_name]['theta'].append(data['theta'])
    new_subject_level_concatenations_pt[subj_name]['delta'].append(data['delta'])
    
    new_subject_level_concatenations_pt[subj_name]['theta_strict'].append(data['coeff_fifth_detail_theta'])
    
    new_subject_level_concatenations_pt[subj_name]['labels'].append(data['labels'])
    
    # Aggiorna il soggetto precedente
    previous_subject_suffix = subject_suffix

# Dopo aver iterato su tutte le condizioni, concatenare e stampare le informazioni dell'ultimo soggetto
if previous_subject_suffix is not None:
    
    last_subject_name = f'pt_{previous_subject_suffix}'
    #levels = subject_level_concatenations_pt[last_subject_name]
    levels = new_subject_level_concatenations_pt[last_subject_name]
    
    print(f"\n\n\t\t\t\t\033[1mConcatenazioni per il soggetto corrente ('{last_subject_name}'):\033[0m\n")
    
    # Concatenazione dei dati dell'ultimo soggetto
    theta_concat = np.concatenate(levels['theta'], axis=0)
    delta_concat = np.concatenate(levels['delta'], axis=0)
    
    theta_concat_strict = np.concatenate(levels['theta_strict'], axis=0)
    
    labels_concat = np.concatenate(levels['labels'], axis=0)
    
    #'''OLD'''
    # Salvataggio dei dati concatenati dell'ultimo soggetto nel dizionario come array NumPy
    #subject_level_concatenations_pt[last_subject_name] = {
    #    'theta': theta_concat,
    #    'delta': delta_concat,
    #    'labels': labels_concat
    #}
    
    #'''NEW'''
    # Salvataggio dei dati concatenati dell'ultimo soggetto nel dizionario come array NumPy
    new_subject_level_concatenations_pt[last_subject_name] = {
       'theta': theta_concat,
        'delta': delta_concat,
        'theta_strict': theta_concat_strict,
        'labels': labels_concat
    }
    
    
    print(f"Soggetto: \033[1m{last_subject_name}\033[0m, "
          f"Theta shape: \033[1m{np.concatenate(levels['theta'], axis=0).shape}\033[0m, "
          f"Delta shape: \033{np.concatenate(levels['delta'], axis=0).shape}\033[0m, "
          f"Labels length: \033[1m{len(np.concatenate(levels['labels'], axis=0))}\033[0m\n\n")



In [ ]:
!pwd

In [ ]:
#Salvo ricostruzioni 4° e 5° livello per singolo terapista con concatenazioni dati e labels 

    
''' PATH  --> cd Plots_Sliding_Estimator_MNE '''
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('subject_level_concatenations_pt.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations_pt, f)
    
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE '''
import pickle
# Salvare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_pt, f)

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''

#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
#    new_subject_level_concatenations_pt = pickle.load(f)
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

In [ ]:
'''CHIAVI DI TUTTO IL DIZIONARIO '''
#subject_level_concatenations_th.keys()


new_subject_level_concatenations_pt.keys()


#SOGGETTO 1

#CHIAVI
#subject_level_concatenations_pt['pt_1'].keys()

#DATI
#subject_level_concatenations_pt['pt_1']['theta'].shape

#new_subject_level_concatenations_pt['pt_1']['theta'].shape

#subject_level_concatenations_pt['pt_1']['delta'].shape

#LABELS
#subject_level_concatenations_pt['th_1']['labels'].shape)
#type(subject_level_concatenations_th['th_1']['labels'])

# Check della concantenazione delle labels PT_1

#subject_level_concatenations_pt['th_1']['labels'][:42]
#subject_level_concatenations_pt['th_1']['labels'][41:81]
#subject_level_concatenations_pt['th_1']['labels'][81:120]
#subject_level_concatenations_pt['th_1']['labels'][121:164]

In [ ]:
#subject_level_concatenations_pt['pt_15']['labels'].shape

In [ ]:
#subject_level_concatenations_pt['pt_1'].keys()

new_subject_level_concatenations_pt['pt_1'].keys()


In [ ]:
#unique_values, counts = np.unique(subject_level_concatenations_pt['pt_1']['labels'], return_counts=True)

#unique_values, counts = np.unique(new_subject_level_concatenations_pt['pt_1']['labels'], return_counts=True)

In [ ]:
#unique_values
#counts
#counts[0]

In [ ]:
!pwd

In [ ]:
# Caricare l'intero dizionario annidato con pickle
with open('new_all_th_concat_reconstructions.pkl', 'rb') as f:
    new_all_th_concat_reconstructions = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('new_all_pt_concat_reconstructions.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions = pickle.load(f)
    
#new_all_th_concat_reconstructions['all_th_fourth'].shape

In [ ]:
# Caricare l'intero dizionario annidato con pickle
with open('new_single_th_all_extracted_reconstructions.pkl', 'rb') as f:
    new_single_th_all_extracted_reconstructions = pickle.load(f)

In [ ]:
new_single_th_all_extracted_reconstructions.keys()

### STEP 5.3.1 - All Patients EEG Data Reconstructions across **Couples of Experimental Conditions**

#### Concatenazione All Single Subject Data (PT) per Coppie di Condizioni Sperimentali

In [ ]:
!pwd

In [ ]:
import pickle
import numpy as np

# Caricare l'intero dizionario annidato con pickle
with open('new_single_pt_all_extracted_reconstructions.pkl', 'rb') as f:
    new_single_pt_all_extracted_reconstructions = pickle.load(f)

In [ ]:
new_single_pt_all_extracted_reconstructions.keys()

In [ ]:
new_single_pt_all_extracted_reconstructions['wave_baseline_1'].keys()

#### Spiegazione STEP 5.3.1 - All Patients EEG Data Reconstructions across Couples of Experimental Conditions

##### **Concatenazione All Single Subject Data (TH) per Coppie di Condizioni Sperimentali**

<br>

In questo caso, voglio **trasformare le variabili che contengono i miei dati e labels delle 4 condizioni sperimentali assieme**, in modo **da creare sottoinsiemi per ogni possibile coppia di condizioni sperimentali**. 

Dunque quello che si dovrà fare **per ogni coppia**:

1) **Filtrare i dati e le etichette**:

- **Estrarre** i dati associati **SOLO alle DUE condizioni in esame** (ad esempio 0 e 1, oppure 1 e 2).
- **Creare un nuovo array di etichette** e **un array di dati** ***corrispondenti*** **SOLO a quelle DUE condizioni**.

2) **Ripetere questa operazione per OGNI combinazione**:

- **Assicurarsi di considerare tutte le coppie** di condizioni sperimentali **SENZA ripetizioni** (ad esempio, non serve processare sia 0 vs 1 che 1 vs 0, perché sono equivalenti!).

3) **Creare quindi una struttura organizzata**, che contenga i dati e le etichette separatamente per ogni coppia, per ciascun livello di ricostruzione (theta, delta, theta_strict).

<br>

Quindi l'obiettivo è di modificare la procedura in modo da **concatenare SOLO le coppie di condizioni sperimentali per OGNI soggetto**. 

Per fare questo, possiamo utilizzare un **approccio combinatorio** per generare **tutte le possibili coppie di condizioni**.


Per quanto riguarda il calcolo combinatorio, possiamo usare il concetto di combinazioni per selezionare le coppie. 
Se hai 4 condizioni, il numero di combinazioni di coppie di condizioni (senza ripetizioni) si calcola come:

$$
\binom{4}{2} = \frac{4!}{2!(4-2)!} = 6
$$


Quindi, con 4 condizioni sperimentali, le combinazioni di coppie di condizioni saranno 6, e queste coppie sono:

(condizione 1, condizione 2) = 'baseline vs th_resp'
(condizione 1, condizione 3) = 'baseline vs pt_resp'
(condizione 1, condizione 4) = 'baseline vs shared_resp'
(condizione 2, condizione 3) = 'th_resp vs pt_resp'
(condizione 2, condizione 4) = 'th_resp vs shared_resp'
(condizione 3, condizione 4) = 'pt_resp vs shared_resp' 


<br>

Piano di modifiche al codice:

1) **Creazione delle coppie di condizioni**: Per ogni soggetto, genereremo tutte le coppie possibili di condizioni sperimentali. Utilizzeremo itertools.combinations per ottenere queste coppie.

2) **Concatenazione per ciascuna coppia**: Per ogni coppia di condizioni, concatenare i dati e le etichette delle due condizioni selezionate.

3) **Salvataggio delle concatenazioni**: Creeremo un dizionario per ciascuna coppia di condizioni per ogni soggetto.


**N.B.**

Nel codice che sto creando...

Ho fatto in modo che ci sia il modo di capire, **per ogni coppia di condizione sperimentale di dati e labels**, a quali condizione sperimentali di dati e labels ci si riferisca, mi spiego:

Sviluppo un **modo "standardizzato" per il quale per OGNI coppia di condizione sperimentale, la variabile che conterrà i dati e labels associate, sia chiamata in un certo modo**...

E nello specifico **con il nome delle DUE condizioni sperimentali che conterranno quei dati e relative labels**...

Del tipo: 

- se è baseline vs th_resp, la variabile sarà "baseline_vs_th_resp"
- se è baseline vs pt_resp, la variabile sarà "baseline_vs_pt_resp"
- se è baseline vs shared_resp, la variabile sarà "baseline_vs_shared_resp"


Senza contare che, questo **processo di standardizzazione del nome delle variabili**, deve esser fatto **per ogni livello di ricostruzione dei dati (sia 4° e 5° livello a partire dai coefficienti di approssimazione, che dal 5 ° livello dei coefficienti di dettaglio)**..

Questo significherebbe che, **per ogni soggetto**, dovrei (o potrei insomma) creare **un dizionario**, che 

- Contenga delle **sotto-chiavi di secondo ordine** (che son theta, delta e theta_strict) e dentro ognuna di queste
- Ci siano contenute **le relative 6 sotto-sotto-chiavi di terzo ordine**, relative ai dati e alle labels associate (anch'esse concatenate ovviamente) delle diverse combinazioni di condizioni sperimentali...


Ossia, vogliamo creare un dizionario strutturato che rappresenti ogni combinazione di coppie di condizioni sperimentali per ciascun soggetto, separando i dati e le etichette per i vari livelli di ricostruzione (theta, delta, theta_strict). 

Ogni combinazione di condizioni sperimentali sarà memorizzata in una chiave strutturata, come ad esempio "baseline_vs_th_resp", e all'interno di ciascuna chiave avremo le informazioni per i vari livelli di ricostruzione.


<br>


#### Esempio di Struttura proposta per il dizionario:


- Soggetto: ad esempio "th_1".
- Livelli di ricostruzione: theta, delta, theta_strict.
- Combinazioni di condizioni sperimentali: per ciascun livello di ricostruzione, avremo sotto-chiavi per ogni coppia di condizioni.

        new_subject_level_concatenations = {
            'th_1': {
                'theta': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                },
                'delta': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                },
                'theta_strict': {
                    'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                    # Altre combinazioni...
                }
            }
        }

<br>

**SOTTO-STEP 1: IDENTIFICAZIONE DELLE STRINGA NUMERICHE PER LA CREAZIONE DELLE VARIABILI - FUTURE CHIAVI - CHE CONTENGONO LE COPPIE DI DATI E LABELS DELLE RELATIVE COPPIE DI CONDIZIONI SPERIMENTALI CONSIDERATE NEL CICLO CORRENTE DEL LOOP**

Aspetta, ci sono altre cose che dovrebbero esser integrate nel codice...

cominciamo dalla prima, che è relativa all' "inferire" diciamo il nome da fornire alla variabile che conterrà i dati e labels delle due condizioni sperimentali correnti... e deve esser fatto, a partire dal nome delle chiavi di 

"new_single_th_all_extracted_reconstructions"...

ora, le sue chiavi son queste

dict_keys(['wave_baseline_1', 'wave_th_resp_1', 'wave_pt_resp_1', 'wave_shared_resp_1', 'wave_baseline_2', 'wave_th_resp_2', 'wave_pt_resp_2', 'wave_shared_resp_2', 'wave_baseline_3', 'wave_th_resp_3', 'wave_pt_resp_3', 'wave_shared_resp_3', 'wave_baseline_4', 'wave_th_resp_4', 'wave_pt_resp_4', 'wave_shared_resp_4', 'wave_baseline_5', 'wave_th_resp_5', 'wave_pt_resp_5', 'wave_shared_resp_5', 'wave_baseline_6', 'wave_th_resp_6', 'wave_pt_resp_6', 'wave_shared_resp_6', 'wave_baseline_7', 'wave_th_resp_7', 'wave_pt_resp_7', 'wave_shared_resp_7', 'wave_baseline_8', 'wave_th_resp_8', 'wave_pt_resp_8', 'wave_shared_resp_8', 'wave_baseline_9', 'wave_th_resp_9', 'wave_pt_resp_9', 'wave_shared_resp_9', 'wave_baseline_10', 'wave_th_resp_10', 'wave_pt_resp_10', 'wave_shared_resp_10', 'wave_baseline_11', 'wave_th_resp_11', 'wave_pt_resp_11', 'wave_shared_resp_11', 'wave_baseline_12', 'wave_th_resp_12', 'wave_pt_resp_12', 'wave_shared_resp_12'])


ora, il modo in cui si identifica un certo soggetto (ossia la chiavi di "primo ordine" che indentificano il soggetto, ossia ad esempio 'th_1'), dipenderebbe dal numero stringa che c'è alla fine di ogni nome stringa di ogni chiave dentro "new_single_th_all_extracted_reconstructions", mi spiego:

il codice dovrebbe capire che, ad esempio, solo l'ultima carattere stringa di queste prime 4 chiavi:

'wave_baseline_1', 'wave_th_resp_1', 'wave_pt_resp_1', 'wave_shared_resp_1', 

si riferisca al soggetto 1, ossia al futuro "th_1"...


per il soggetto 2, sarebbero: 

'wave_th_resp_2', 'wave_pt_resp_2', 'wave_shared_resp_2', e così via per gli altri soggetti..


Facendo attenzione al fatto che, dopo il soggetto 9, ovviamente, si passerà alle decine (a livello numerico), per cui saranno gli ultime due caratteri da considerare per l'identificazione delle sue rispettive chiavi, che in quel caso saranno per il soggetto 10, ossia il futuro th_10

'wave_baseline_10', 'wave_th_resp_10', 'wave_pt_resp_10', 'wave_shared_resp_10',

Inoltre, poi, per creare le variabili associate alle coppie di dati e labels delle relative condizioni sperimentali, dovrà il codice far in modo che il nome di quella variabile dipenda dalle stringhe sempre che si riferiscono al nome delle due chiavi di "new_single_th_all_extracted_reconstructions" da cui preleva i dati e le labels... 

ad esempio, se deve creare la variabile dei dati 'baseline_vs_th_resp" del primo soggetto, le chiavi rispettive da cui deve andare a prelevare le stringhe saranno appunto "'wave_baseline_1'" e "'wave_th_resp_1'"....

diciamo che si potrebbe creare una lista di stringhe che sarà del tipo:

experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp'], per vedere se una di queste sia dentro la rispettiva chiave di  new_single_th_all_extracted_reconstructions su cui sta iterando, che nel nostro caso di esempio sarebbero sempre

'wave_baseline_1' (e da cui vede che c'è la stinga 'baseline')
'wave_th_resp_1' (e da cui vede che c'è la stinga 'th_resp')

è chiaro?


<br>

In sostanza, desideri un modo per inferire dinamicamente il nome del soggetto e delle variabili che conterranno i dati e le etichette per ogni combinazione di condizioni, a partire dal nome delle chiavi di new_single_th_all_extracted_reconstructions. Ecco un piano per raggiungere questo obiettivo:

Passaggi:

- Identificare il soggetto:

Le chiavi di new_single_th_all_extracted_reconstructions finiscono con un numero che identifica il soggetto (es. wave_baseline_1, wave_th_resp_1, wave_pt_resp_1).
Questo numero può essere estratto dalle ultime cifre della chiave (ad esempio, 1 da wave_baseline_1).
La variabile associata a ciascun soggetto sarà chiamata th_X, dove X è il numero del soggetto.

- Generare dinamicamente il nome delle variabili:

A partire dai nomi delle chiavi, possiamo inferire quale combinazione di condizioni sperimentali stiamo trattando (es. baseline_vs_th_resp).
Creeremo una lista delle condizioni (experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']), quindi esamineremo le chiavi per determinare quali condizioni sono presenti.

- Creare il dizionario:

A ciascun soggetto verrà associato un dizionario, e per ogni combinazione di condizioni sperimentali, assoceremo i dati e le etichette in una chiave che seguirà la convenzione del tipo baseline_vs_th_resp.


<br>

Spiegazione:

1) Estrazione delle condizioni e soggetto:

La chiave, ad esempio wave_baseline_1, viene separata in parti. La parte baseline viene estratta per determinare la condizione, mentre 1 indica il numero del soggetto.
Queste informazioni vengono utilizzate per creare il nome del soggetto, th_1.

2) Combinazioni di condizioni:

La lista experimental_conditions contiene le 4 condizioni: baseline, th_resp, pt_resp, shared_resp.
Per ogni soggetto, controlliamo quali condizioni sono disponibili nella chiave (ad esempio, se il soggetto 1 ha wave_baseline_1 e wave_th_resp_1, creiamo la combinazione baseline_vs_th_resp).

3) Creazione dinamica delle variabili:

Utilizziamo la combinazione di condizioni per generare la chiave della variabile (baseline_vs_th_resp).
I dati e le etichette per la combinazione di condizioni vengono estratti e concatenati.


4) Risultato finale:

La struttura finale del dizionario new_subject_level_concatenations avrà una chiave per ciascun soggetto (th_1, th_2, ecc.), e sotto ogni soggetto ci saranno le combinazioni di condizioni per ciascun livello di ricostruzione (theta, delta, theta_strict), con i dati e le etichette corrispondenti.

<br>

Esempio di output:

    {
        'th_1': {
            'theta': {
                'baseline_vs_th_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'baseline_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'baseline_vs_shared_resp': {'data': np.array([...]), 'labels': np.array([...])},
                'th_resp_vs_pt_resp': {'data': np.array([...]), 'labels': np.array([...])},
                # Altre combinazioni...
            },
            'delta': {
                # Stessa struttura per 'delta'
            },
            'theta_strict': {
                # Stessa struttura per 'theta_strict'
            }
        }
    }

 
Questa struttura ti permetterà di avere un'organizzazione chiara e dinamica dei dati per ogni soggetto e combinazione di condizioni sperimentali.
 
 
<br>

**SOTTO-STEP 2: IDENTIFICAZIONE DELLE STRINGA ALFABETICHE PER LA CREAZIONE DELLE VARIABILI - FUTURE CHIAVI - CHE CONTENGONO IL NOME DELLE DUE COPPIE DI CONDIZIONI SPERIMENTALI DI CUI VENGONO PRELEVATI I DATI E LABELS CONCATENATI E CHE VENGONON CONSIDERATE NEL CICLO CORRENTE DEL LOOP**


ok, ora c'è una ultima cosa che mi manca da dirti, che è relativa alla ri-assegnazione del codice numerico associato ad ogni coppia di condizioni sperimentali...

nel senso che, originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò 

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo


print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n")
print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n")
print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n")
print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")


Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza,  nel tuo codice, ho bisogno che 

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre 

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e  e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare le labels andranno ovviamente riconvertite! Perché?
perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempip, in quel caso, le sue labels (che son  originariamente codificate come '1' in 'new_subject_level_concatenations'!) diveteranno '0', mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...


è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?


<br>

La **logica di ri-assegnazione delle etichette (labels)** è chiara e posso integrarla nel codice. 

La logica che stai descrivendo consiste essenzialmente nel **garantire che, quando crei una variabile che contiene dati e etichette per due condizioni sperimentali, le etichette siano sempre "0" per la prima condizione (cond_1) e "1" per la seconda condizione (cond_2)**, 

                **INDIPENDENTEMENTE** da come sono originariamente codificate in **"new_single_th_all_extracted_reconstructions"!
                
                

Ecco come possiamo procedere:

- Identificazione delle condizioni: Come hai descritto, determineremo le due condizioni sperimentali da confrontare, ad esempio "baseline" contro "th_resp", "baseline" contro "pt_resp", ecc.

- Riconversione delle etichette:

 - Se la condizione di confronto è "baseline" (che è associata a 0), non dobbiamo modificare le etichette.
 - Se la condizione di confronto non è "baseline", dovremo riconvertire le etichette di quella condizione a 0 e le etichette della condizione di confronto a 1.

- Struttura del codice: Durante la creazione delle variabili, dovremo controllare quale condizione è la prima (cond_1) e quale è la seconda (cond_2), e applicare questa logica per ri-assegnare le etichette di conseguenza.


<br>

Inoltre


dentro 

"# Crea tutte le combinazioni uniche di condizioni sperimentali (es. 'baseline vs th_resp')
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
"

Effettivamente vengono create delle tuple di coppie di stringhe che corrispondono a quelle con cui dovrebbero esser create le sotto-sotto-chiavi delle coppie di condizioni sperimentali..

tuttavia, è giusto che iteri rispetto a 'condition_pairs', ma deve inserire un qualche controllo anche rispetto a questa cosa:

originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo

print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n") print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n") print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n") print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")

Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza, nel tuo codice, ho bisogno che

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, che nel caso di "condition_pairs" dovrebbe corrispondere ai primi 3 elementi della sua lista no, perché sarebbero 

[('baseline', 'th_resp'), 
    ('baseline', 'pt_resp'), 
    ('baseline', 'shared_resp'), 

è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare, che fa riferimento a questi altri elementi di 
"condition_pairs" che è creato nel loop ossia

('th_resp', 'pt_resp'), 
('th_resp', 'shared_resp'), 
('pt_resp', 'shared_resp')]

le labels andranno ovviamente riconvertite! Perché? 

Perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempio, in quel caso, le sue labels (che son originariamente codificate come '1' in 'new_subject_level_concatenations'!) diventeranno '0',

mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...

è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?dentro "# Crea tutte le combinazioni uniche di condizioni sperimentali (es. 'baseline vs th_resp')
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
    "

effettivamente vengono create delle tuple di coppie di stringhe che corrispondono a quelle con cui dovrebbero esser create le sotto-sotto-chiavi delle coppie di condizioni sperimentali..

tuttavia, è giusto che iteri rispetto a 'condition_pairs', ma deve inserire un qualche controllo anche rispetto a questa cosa:

originariamente...

new_single_th_all_extracted_reconstructions ha queste labels, che se io le vedo avrò

per baseline una serie di 0, per th_resp una serie di 1, per pt_resp, una serie di 2 e per shared_resp una serie di 3, in questo modo

print(f"Baseline in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n") print(f"Th_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n") print(f"Pt_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n") print(f"Shared_Resp in TH_1:, {np.unique(new_single_th_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")

Baseline in TH_1:, (array(['0'], dtype='<U1'), array([51]))

Th_Resp in TH_1:, (array(['1'], dtype='<U1'), array([40]))

Pt_Resp in TH_1:, (array(['2'], dtype='<U1'), array([40]))

Shared_Resp in TH_1:, (array(['3'], dtype='<U1'), array([56]))

di conseguenza, nel tuo codice, ho bisogno che

le labels associate a 'cond_1' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '0', mentre

le labels associate a 'cond_2' (quando crei la relativa variabile delle due condizioni sperimentali di cui vengono concatenati i dati e le labels) siano riconvertite sempre in '1'

questo aspetto è importante, per quando crei le variabili che conterranno le coppie di dati condizioni sperimentali...

ora, nel caso in cui tu stia considerando magari baseline vs le altre condizioni sperimentali, che nel caso di "condition_pairs" dovrebbe corrispondere ai primi 3 elementi della sua lista no, perché sarebbero 

[('baseline', 'th_resp'), 
    ('baseline', 'pt_resp'), 
    ('baseline', 'shared_resp'), 

è chiaro che in quel caso specifico, ad esempio, baseline sarà sempre la stringa associata a 'cond_1' e quindi in quel caso sarà sempre 0, e quindi sarebbe apposto..

ma per gli altri casi di confronto di baseline rispetto alle altre 3 condizioni sperimentali, è chiaro che se sarà th_resp la condizione di confronto, allora in quel caso di quella specifica variabile, le labels non avranno bisogno di esser diciamo 'ri-convertite' perché già naturalmente diciamo baseline avrà le labels '0' e e th_resp avrà già '1' (come è già originariamente codificato in 'new_subject_level_concatenations'!)

ma nel caso delle altre variabili da creare, che fa riferimento a questi altri elementi di 
"condition_pairs" che è creato nel loop ossia

('th_resp', 'pt_resp'), 
('th_resp', 'shared_resp'), 
('pt_resp', 'shared_resp')]

le labels andranno ovviamente riconvertite! Perché? 

Perché ovviamente nel caso sia la th_resp la 'cond_1', ad esempio, in quel caso, le sue labels (che son originariamente codificate come '1' in 'new_subject_level_concatenations'!) diventeranno '0',

mentre le altre condizioni di confronto, una alla volta, diventeranno '1' invece...

è chiara diciamo la logica di ri-assegnazione delle relative labels in sostanza?



#### Implementazione STEP 5.3.1 - All Patients EEG Data Reconstructions across Couples of Experimental Conditions

In [ ]:
new_single_pt_all_extracted_reconstructions.keys()

In [ ]:
new_single_pt_all_extracted_reconstructions['wave_baseline_1'].keys()

In [ ]:
type(new_single_pt_all_extracted_reconstructions['wave_baseline_1']['theta'])

In [ ]:
print(f"Baseline in PT_1:, {np.unique(new_single_pt_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n")
print(f"Th_Resp in PT_1:, {np.unique(new_single_pt_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n")
print(f"Pt_Resp in PT_1:, {np.unique(new_single_pt_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n")
print(f"Shared_Resp in PT_1:, {np.unique(new_single_pt_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")

In [ ]:
new_single_pt_all_extracted_reconstructions['wave_baseline_1'].keys()

In [ ]:
'''DETAILED VERSION WITH COMPLICATED PRINTS'''

import itertools
import numpy as np

experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']

# Nuova variabile per tracciare il soggetto corrente stampato
last_subject_key = None

# Dizionario per tenere traccia delle combinazioni già stampate per ogni soggetto
printed_combinations = {}

# Nuova variabile per memorizzare i risultati di dati e labels concatenati di coppie di condizioni sperimentali
new_subject_level_concatenations_coupled_exp_pt = {}

# Loop su tutte le chiavi del dizionario iniziale
for key in new_single_pt_all_extracted_reconstructions.keys():

    key_parts = key.split('_')
    subject_number = key_parts[-1] if key_parts[-1].isdigit() else None  # Verifica se è numerico
    
    # Verifica che il numero del soggetto sia valido
    if subject_number is None:
        continue  # Salta chiavi non valide
    
    subject_key = f"pt_{subject_number}"  # Es. 'th_1' o 'th_12'
    
    '''PER TRACCIARE SOGGETTO PRECEDENTE'''
    # Aggiungi separazione visiva quando cambia il soggetto
    if subject_key != last_subject_key:
        if last_subject_key is not None:  # Evita di stampare separatori prima del primo soggetto
            print("\n" + "-" * 50 + f" END OF {last_subject_key.upper()} " + "-" * 50 + "\n")
        print(f"\nProcessing Subject: {subject_key}\n" + "=" * 80)
        
        # Inizializza il dizionario delle combinazioni stampate per il nuovo soggetto
        printed_combinations[subject_key] = set()  # Usando un set per evitare duplicati
    
    last_subject_key = subject_key  # Aggiorna il soggetto corrente
    
    # Inizializza la struttura se non esiste ancora
    if subject_key not in new_subject_level_concatenations_coupled_exp_pt:
        new_subject_level_concatenations_coupled_exp_pt[subject_key] = {'theta': {}, 'delta': {}, 'theta_strict': {}}
    
    # Crea tutte le combinazioni uniche di condizioni sperimentali (es. 'baseline vs th_resp')
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
    
    # Loop sulle combinazioni
    for cond_1, cond_2 in condition_pairs:
        
        # Crea il nome della variabile per la combinazione
        condition_pair_key = f"{cond_1}_vs_{cond_2}"
        
        # Controlla se la combinazione è già stata stampata per il soggetto corrente
        if condition_pair_key in printed_combinations[subject_key]:
            continue  # Salta la combinazione se è già stata stampata
        
        # Stampa il messaggio per la prima volta che incontriamo questa combinazione
        print(f"\n\t\tCreation of Coupled Condition \033[1m{condition_pair_key}\033[0m")
        
        # Aggiungi la combinazione al set delle combinazioni stampate per il soggetto
        printed_combinations[subject_key].add(condition_pair_key)
        
        # Ora esegui il ciclo sui livelli
        for level in ['theta', 'delta', 'coeff_fifth_detail_theta']:
            
            print(f"\n\t\t\t--- Level: \033[1m{level}\033[0m ---")
             
            # Gestisci il caso per 'coeff_fifth_detail_theta'
            if level == 'coeff_fifth_detail_theta':
                
                # Ottieni i dati e le etichette per il livello coeff_fifth_detail_theta
                data_cond_1 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_1}_{subject_number}", {}).get(level)
                print(f"Extracting data_cond_1 from {cond_1} which is ”wave_{cond_1}_{subject_number}\033[1m[{level}]\033[0m")
                
                labels_cond_1 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_1}_{subject_number}", {}).get('labels')
                print(f"Extracting labels_cond_1 from {cond_1} which is ”wave_{cond_1}_{subject_number}\033[1m[{level}]\033[0m['labels']")
                      
                data_cond_2 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_2}_{subject_number}", {}).get(level)
                print(f"Extracting data_cond_2 from {cond_2} which is ”wave_{cond_2}_{subject_number}\033[1m[{level}]\033[0m")
                
                labels_cond_2 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_2}_{subject_number}", {}).get('labels')
                print(f"Extracting labels_cond_2 from {cond_2} which is ”wave_{cond_2}_{subject_number}\033[1m[{level}]\033[0m['labels']\n")      
                    
            else:
                # Ottieni i dati e le etichette per gli altri livelli (theta, delta)
                data_cond_1 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_1}_{subject_number}", {}).get(level)
                print(f"Extracting data_cond_1 from {cond_1} which is ”wave_{cond_1}_{subject_number}\033[1m[{level}]\033[0m")
                
                labels_cond_1 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_1}_{subject_number}", {}).get('labels')
                print(f"Extracting labels_cond_1 from {cond_1} which is ”wave_{cond_1}_{subject_number}\033[1m[{level}]\033[0m['labels']")
                 
                data_cond_2 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_2}_{subject_number}", {}).get(level)
                print(f"Extracting data_cond_2 from {cond_2} which is ”wave_{cond_2}_{subject_number}\033[1m[{level}]\033[0m")
                
                labels_cond_2 = new_single_th_all_extracted_reconstructions.get(f"wave_{cond_2}_{subject_number}", {}).get('labels')
                print(f"Extracting labels_cond_2 from {cond_2} which is ”wave_{cond_2}_{subject_number}\033[1m[{level}]\033[0m['labels']\n")
                
            # Verifica che i dati siano validi
            if data_cond_1 is None or labels_cond_1 is None or data_cond_2 is None or labels_cond_2 is None:
                continue  # Salta combinazioni incomplete

            # Riassegna le etichette per garantire che "cond_1" = 0 e "cond_2" = 1
            labels_cond_1 = np.zeros_like(labels_cond_1, dtype=int)  # Tutte 0
            labels_cond_2 = np.ones_like(labels_cond_2, dtype=int)   # Tutte 1

            # Concatenazione dei dati e delle etichette
            concatenated_data = np.vstack((data_cond_1, data_cond_2))
            concatenated_labels = np.hstack((labels_cond_1, labels_cond_2))

            # Salva i risultati nella struttura
            if level == 'coeff_fifth_detail_theta':
                # Salva i dati sotto 'theta_strict' per 'coeff_fifth_detail_theta'
                new_subject_level_concatenations_coupled_exp_pt[subject_key]['theta_strict'][condition_pair_key] = {
                    'data': concatenated_data,
                    'labels': concatenated_labels}
            else:
                # Salva i dati sotto i livelli 'theta' o 'delta'
                new_subject_level_concatenations_coupled_exp_pt[subject_key][level][condition_pair_key] = {
                    'data': concatenated_data,
                    'labels': concatenated_labels}
    
        # Dopo aver trattato tutti i livelli, aggiungi una separazione visiva per il soggetto
        print("-" * 50 + f"-" * 50)


In [ ]:
print(f"\t\t\t\t\033[1mStructure of new_subject_level_concatenations_coupled_exp_pt\033[0m: \n")
print(f"\033[1mFirst Order Keys\033[0m: {new_subject_level_concatenations_coupled_exp_pt.keys()}\n")
print(f"\033[1mSecond Order Keys\033[0m: {new_subject_level_concatenations_coupled_exp_pt['pt_1'].keys()}\n")
print(f"\033[1mThird Order Keys\033[0m: \n{new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta'].keys()}\n")
print(f"\033[1mFourth Order Keys\033[0m: \n{new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp'].keys()}\n")

In [ ]:
'''VERIFICO CHE LA CONCATENAZIONE SIA AVVENUTA CORRETTAMENTE!'''

print("\tNOW, LET US SEE IF THE CONCATENATIONS RESPECT THE ORIGINAL SHAPES FOR EVERY COUPLED EXPERIMENTAL CONDITION!\n")
print("\tFOR THE 1°ST SUBJECT: CHECK IF THE SUM OF INDIVIDUAL EXP COND SHAPE MATCHES THE COUPLED COND CONCATENATION SHAPE:\n\n")

print("\033[1mINDIVIDUAL EXP COND SHAPE OF FIRST SUBJECT\033[0m:")


print(f"Baseline in PT_1:, {np.unique(new_single_pt_all_extracted_reconstructions['wave_baseline_1']['labels'], return_counts = True)}\n")
print(f"Th_Resp in PT_1:, {np.unique(new_single_pt_all_extracted_reconstructions['wave_th_resp_1']['labels'], return_counts = True)}\n")
print(f"Pt_Resp in PT_1:, {np.unique(new_single_pt_all_extracted_reconstructions['wave_pt_resp_1']['labels'], return_counts = True)}\n")
print(f"Shared_Resp in PT_1:, {np.unique(new_single_pt_all_extracted_reconstructions['wave_shared_resp_1']['labels'], return_counts = True)}\n")
print()

#new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['data'].shape

# Seleziona il primo soggetto (ad esempio, 'th_1')
subject_key = 'pt_1'

# Itera per ogni livello e condizione sperimentale
for level in ['theta', 'delta', 'theta_strict']:
    print(f"\nShape of Coupled Experimental Data and Labels based on DWT Reconstructed Level \033[1m{level}\033[0m for subject \033[1m{subject_key}\033[0m\n")

    # Itera per ogni coppia di condizioni sperimentali
    for condition_pair_key, data_labels in new_subject_level_concatenations_coupled_exp_pt[subject_key][level].items():
        
        # Estrai i dati e le etichette per ogni coppia di condizioni
        data = data_labels.get('data')
        labels = data_labels.get('labels')

        # Stampa il nome della coppia di condizioni e le loro dimensioni
        print(f"Condition Pair: \033[1m{condition_pair_key}\033[0m")
        
        if data is not None and labels is not None:
            print(f"  Data Shape: {data.shape}")
            print(f"  Labels Shape: {labels.shape}")
        else:
            print("  Missing data or labels!")

In [ ]:
print(np.unique(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp']['labels'], return_counts = True))
print(np.unique(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta_strict']['th_resp_vs_shared_resp']['labels'], return_counts = True))

In [ ]:
print(f"\t\t\t\033[1mBASELINE_VS_TH_RESP\033[0m\n")
print(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp']['labels'][:44])
print(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp']['labels'][45:])
print()
print()
print(f"\t\t\t\033[1mTH_RESP_VS_SHARED_RESP\033[0m\n")
print(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['th_resp_vs_shared_resp']['labels'][:40])
print(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['th_resp_vs_shared_resp']['labels'][41:])


#### STEP 5.3.1.2 - Salvataggio Dataset di All Single Patients EEG Data Reconstructions across Couples of Experimental Conditions

In [ ]:
!pwd

In [ ]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_NF '''
import pickle

# Salvare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_coupled_exp_pt, f)

### STEP 5.3.2 - Mi concateno le strutture dati e labels dei singoli Patients EEG Data Reconstructions across **Couples of Experimental Conditions** INSIEME

#### Concatenazione All Single Subject Data (PT) per Coppie di Condizioni Sperimentali INSIEME

In [ ]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE'''

import pickle

path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{path}/new_subject_level_concatenations_coupled_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt = pickle.load(f)

In [ ]:
#new_subject_level_concatenations_coupled_exp_pt.keys()
#new_subject_level_concatenations_coupled_exp_pt['th_1'].keys()
#new_subject_level_concatenations_coupled_exp_pt['th_1']['theta'].keys()
#new_subject_level_concatenations_coupled_exp_pt['th_1']['theta']['baseline_vs_th_resp'].keys()
#np.unique(new_subject_level_concatenations_coupled_exp_pt['th_1']['theta']['baseline_vs_th_resp']['labels'], return_counts = True)

In [ ]:
##NEW OFFICIAL VERSION!

#SENZA DICT_NAME!

import numpy as np

def concatenate_all_single_subj_wavelets_coupled_experimental_conditions_pt(data_structure, wavelet_levels, conditions):
    
    """
    Concatena i dati e le etichette per ogni condizione sperimentale da una struttura dati con un livello in più,
    dove questo livello rappresenta le diverse coppie di condizioni sperimentali iterate nel ciclo ossia
    
    'baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 
    'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'
    
    ordinandoli anche per etichetta.
    
    Questo perché ogni array di labels avrà sempre o 0 od 1 come etichette,
    dato che son coppie di condizioni sperimentali

    Parameters:
        data_structure (dict): La struttura dati di input che contiene i dati per soggetti e condizioni.
        conditions (list): Le condizioni sperimentali (chiavi del secondo livello) da processare.
        

    Returns:
        dict: Un dizionario contenente i nuovi dizionari con 
        i dati concatenati e le etichette per ogni coppia di condizioni sperimentali
    
    """
        
        
    # Dizionario per contenere i dati concatenati di tutti i soggetti
    all_subj_data_by_coupled_cond = {}
    
    # Itera su ogni livello di ricostruzione wavelet ('theta', 'delta', 'theta_strict')
    
    for reconstruction_level in wavelet_levels:
        
        all_subj_data_by_coupled_cond[reconstruction_level] = {}  # Struttura annidata per livello

        # Itera su ogni coppia di condizioni sperimentali
        for condition_pair in conditions:
            
            #Dizionari per raccogliere dati e labels ordinati per ogni coppia di condizioni sperimentali
            # che è dinamico, per ogni coppia di condizioni sperimentali 
            #(quindi si ricreeranno passando alla condizione sperimentale successiva!)
            
            data_by_label = {}
            labels_by_label = {}
            shape_labels_per_subject = {0: [], 1: []}  # Inizializza il dizionario per 0 e 1

            # Itera su tutti i soggetti
            # In questo caso, itera sulle chiavi di ogni soggetto

            # Quindi prenderà, per la relativa coppia di condizioni sperimentali di ogni soggetto,
            # i dati e le labels di quel soggetto, per quella relativa coppia di condizioni sperimentali
            
            for subject_key in data_structure.keys():
                
                # Controlla se il livello di ricostruzione esiste per il soggetto
                if reconstruction_level not in data_structure[subject_key]:
                    continue
                    
                # Controlla se il livello di ricostruzione esiste per il soggetto
                if condition_pair not in data_structure[subject_key][reconstruction_level]:
                    continue
                
                # Qui estrae i dati e le labels per questa condizione sperimentale di quel soggettio lì
                subject_data = data_structure[subject_key][reconstruction_level][condition_pair]['data']
                subject_labels = data_structure[subject_key][reconstruction_level][condition_pair]['labels']
                
                # Trova le etichette uniche e gli indici corrispondenti per quella coppia di condizioni sperimentali lì,
                # Ossia, potrà trovare gli 0 e gli 1 
                
                unique_labels = np.unique(subject_labels)
                
                #A quel punto, per ognuna delle due labels trovate per quella coppia di condizioni sperimentali lì
                #Che saranno sempre o 0 o 1
                
                for label in unique_labels:
                    
                    # Trova gli indici dei dati corrispondenti a questa etichetta
                    # Una volta per lo 0 ed una volta per l' 1
                    
                    label_indices = np.where(subject_labels == label)[0]
                    
                    # A quel punto, estrae i dati e le labels per questi indici
                    # Una volta per lo 0 ed una volta per l' 1
                    
                    data_for_label = subject_data[label_indices]
                    labels_for_label = subject_labels[label_indices]
                    
                    # A quel punto, per ogni soggetto, per ogni condzione sperimentale, 
                    # per quelle due labels là (sempre presenti, per ogni coppia di condizioni sperimentali)
                    # Una volta per lo 0 ed una volta per l' 1

                    #Andrà a creare per ogni etichetta, una chiave che si chiamerà 
                    #o 0 od 1 (inizialmente, vuoto -> perché deve esser inizializzato)
                    #E poi, dopo, ci appenderà le labels 
                     # Una volta per lo 0 ed una volta per l' 1
                    #  Di quel soggetto per quella coppia di condizioni sperimentali iterate a quel momento
                    
                    #Aggiunge ai dizionari globali, creando la chiave se non esiste
                    if label not in data_by_label:
                        data_by_label[label] = []
                        labels_by_label[label] = []

                    data_by_label[label].append(data_for_label)
                    labels_by_label[label].append(labels_for_label)
                    
                    # **Salva la shape delle etichette per il soggetto corrente**
                    shape_labels_per_subject[label].append(labels_for_label.shape[0]) # Aggiungi solo la dimensione (numero di etichette)
                    
                    '''PRINT PER CHECK LABELS DI OGNI SOGGETTO PER OGNI COPPIA DI CONDIZIONE CONDIZIONI SPERIMENTALI''' 
                    #print(f"Soggetto: \033[1m{subject_key}\033[0m, Livello: \033[1m{reconstruction_level}\033[0m, Condizione: \033[1m{condition_pair}\033[0m, "
                    #      f"Etichetta: \033[1m{label}\033[0m, Shape: \033[1m{labels_for_label.shape[0]}\033[0m")
                    
                    # **Aggiungi un print di controllo per ogni soggetto**
                    #print(f"Soggetto: \033[1m{subject_key}\033[1m, Livello: {reconstruction_level}, Condizione: {condition_pair}, Etichetta: {label}, Shape: {labels_for_label.shape[0]}")
    
            
            #*** *** *** *** *** *** *** *** *** *** *** *** *** *** ***
            
            # Dopodiché, vado a creare invece i dizionari che conterranno
            # Le concatenazioni, di dati e labels corrispondenti, di tutti i soggetti per cui l'etichetta era 
            # o 0 od 1 

            # Di conseguenza, qui dentro dovrei avere, per ogni coppia di condizioni sperimentali
            # Tutti gli 0 ed 1 (ed i relativi dati corrispondenti)
            # di tutti i soggetti, ma concatenati

            concatenated_data_by_label = {}
            concatenated_labels_by_label = {}

            #for label in data_by_label.keys():
            #    if len(data_by_label[label]) > 0:  # Evita errori di concatenazione
            #        concatenated_data_by_label[label] = np.vstack(data_by_label[label])
            #        concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
            
            for label in data_by_label.keys():
                concatenated_data_by_label[label] = np.vstack(data_by_label[label])
                concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])

                # **Calcolare la shape totale delle etichette**
                #total_labels_0 = np.sum(1 for subject_labels in labels_by_label[label] if 0 in subject_labels)
                #total_labels_1 = np.sum(1 for subject_labels in labels_by_label[label] if 1 in subject_labels)
                #total_labels = total_labels_0 + total_labels_1

                # **Determinare gli indici delle etichette 0 e 1 nell'array finale**

                # Gli indici delle etichette 0
                indices_labels_0 = np.where(concatenated_labels_by_label[label] == 0)[0]

                # Gli indici delle etichette 1
                indices_labels_1 = np.where(concatenated_labels_by_label[label] == 1)[0]
                
                # Indici iniziale e finale per le etichette 0 e 1
                start_idx_0 = indices_labels_0[0] if len(indices_labels_0) > 0 else None
                end_idx_0 = indices_labels_0[-1] if len(indices_labels_0) > 0 else None
                start_idx_1 = indices_labels_1[0] if len(indices_labels_1) > 0 else None
                end_idx_1 = indices_labels_1[-1] if len(indices_labels_1) > 0 else None


                # **Print finale per verificare la concatenazione per ogni label**
                #print(f"\nCondizione: \033[1m{condition_pair}\033[0m, Etichetta: {label}")
                #print(f"  - Shape dei dati concatenati per \033[1m{label}\033[0m: {concatenated_data_by_label[label].shape}")
                #print(f"  - Shape delle etichette concatenate per \033[1m{label}\033[0m: {concatenated_labels_by_label[label].shape}")

                # **Stampa la lista delle shapes delle etichette per ogni soggetto per questa etichetta**
                #print(f"\n  - Shape delle etichette per soggetto (per etichetta {label}): {shape_labels_per_subject[label]}\n")


                # **Stampa il conteggio totale delle etichette**
                #print(f"\n  - Totale delle etichette 0: {total_labels_0}")
                #print(f"  - Totale delle etichette 1: {total_labels_1}")
                #print(f"  - Totale delle etichette per la condizione: {total_labels}\n")

                # **Stampa gli indici per le etichette 0 e 1**
                # **OSSIA --> Stampa gli indici per l'etichetta corrente**

                #if label == 0:
                #    print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
                #else:
                #    print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}\n")


                #print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
                #print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}")


            #ARRIVATI FINO A QUI, abbiamo che siccome stiamo iterando prima per tutti gli 0 e poi per tutti gli 1
            #Significa che, assumendo che siamo dentro 'baseline_vs_th_resp' e che 

            #'baseline' sia rappresentato dalle etichette 0
            #'th_resp' sia rappresentato dalle etichette 1

            #Al PRIMO ciclo avrò che:

            #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti)
            #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'baseline' per 'baseline_vs_th_resp'di tutti i soggetti)

            #Al SECONDO ciclo avrò che:

            #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
            #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)

            #Quindi mi manca ancora 

            #A) CONCATENARE I DATI:

            #1)prima tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 

            #CON

            #2)tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)

            #che verrà fatto dentro all_data (che è anch'esso una variabile dinamica!)

            #B) CONCATENARE LE LABELS:

            #1)prima tutti le labels (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 

            #CON

            #2)tutti le labels (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)

            #che verrà fatto dentro all_labels (che è anch'esso una variabile dinamica!)

            # Liste per raccogliere dati e labels di tutte le etichette

            # Qui dentro, invece, dov con
            
            all_data = []
            all_labels = []

            for label in concatenated_data_by_label.keys():
                all_data.append(concatenated_data_by_label[label])
                all_labels.append(concatenated_labels_by_label[label])
            
            #Alla fine, qui dentro avrò che, PER OGNI COPPIA DI CONDIZIONI SPERIMENTALI


            #'final_data' dovrebbe avere 
                #- prima tutti i dati di tutti i soggetti associati all'etichetta 0 
                #- e poi tutti i dati di tutti i soggetti associati all'etichetta 1

            #'final_labels' dovrebbe avere 
                #- prima tutte le labels di tutti i soggetti associati all'etichetta 0
                #- e poi tutte tutte le labels di tutti soggetti associati all'etichetta 1...
                
            if all_data:  # Evita errori di concatenazione se non ci sono dati
                final_data = np.vstack(all_data)
                final_labels = np.hstack(all_labels)
                
                all_subj_data_by_coupled_cond[reconstruction_level][condition_pair] = {
                    'data': final_data,
                    'labels': final_labels
                }
                

    #print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")

    #for reconstruction_level, conditions_dict in all_subj_data_by_coupled_cond.items():
    #    for condition_pair, value in conditions_dict.items():
    #        labels = value['labels']
    #        unique_labels = np.unique(labels)
    #        total_labels = 0

    #        print(f"\nLivello Wavelet: {reconstruction_level}, Condizione: {condition_pair}")
    #        for label in unique_labels:
    #            label_indices = np.where(labels == label)[0]
    #            start_idx = label_indices[0] if len(label_indices) > 0 else None
    #            end_idx = label_indices[-1] if len(label_indices) > 0 else None
    #            total_labels += len(label_indices)

    #            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m "
    #                  f"(Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

    #        print(f"Totale etichette (0 e 1): \033[1m{total_labels}\033[0m\n")

    return all_subj_data_by_coupled_cond


In [ ]:
# Parametri
conditions = ['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp',
              'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp']


wavelet_levels = ['theta', 'delta', 'theta_strict']

# Chiamata alla funzione, qui definisco a mano il nome della variabile (i.e., 
new_all_pt_concat_reconstructions_wavelet_levels_coupled_exp = concatenate_all_single_subj_wavelets_coupled_experimental_conditions_pt(
    data_structure=new_subject_level_concatenations_coupled_exp_pt,
    wavelet_levels = wavelet_levels,
    conditions=conditions
)

print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")

for reconstruction_level, conditions_dict in new_all_th_concat_reconstructions_wavelet_levels_coupled_exp.items():
    for condition_pair, value in conditions_dict.items():
        labels = value['labels']
        unique_labels = np.unique(labels)
        total_labels = 0

        print(f"\nLivello Wavelet: \033[1m{reconstruction_level}\033[0m, Condizione: \033[1m{condition_pair}\033[0m")
        for label in unique_labels:
            label_indices = np.where(labels == label)[0]
            start_idx = label_indices[0] if len(label_indices) > 0 else None
            end_idx = label_indices[-1] if len(label_indices) > 0 else None
            total_labels += len(label_indices)

            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m "
                  f"(Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

        print(f"Totale etichette (0 e 1): \033[1m{total_labels}\033[0m\n")

In [ ]:
#new_concatenated_dictionaries.keys()
#new_concatenated_dictionaries['theta'].keys()
#new_concatenated_dictionaries['theta']['baseline_vs_th_resp'].keys()
#np.unique(new_concatenated_dictionaries['theta']['baseline_vs_th_resp']['labels'], return_counts = True)

#### STEP 5.3.2.1 - Salvataggio Dataset di **All Single Patients** EEG Data Reconstructions across **Couples of Experimental Conditions** INSIEME

In [ ]:
pwd

In [ ]:
cd ..

In [ ]:
cd all_datas

In [ ]:
''' PATH  --> cd Familiar_Wavelet_Reconstructions '''
import pickle
import os
   
base_path = '/home/stefano/Interrogait/all_datas/Familiar_Wavelet_Reconstructions'

# Controlla se la cartella esiste, altrimenti la crea
if not os.path.exists(base_path):
    os.makedirs(base_path)
    
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_wavelet_levels_coupled_exp.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_wavelet_levels_coupled_exp, f)

## STEP 6: Decoding in sensor space : Implementazione mne.decoding.SlidingEstimator
### Classificazione con labels 'vere'

### STEP 6.1.2: Mi salvo le strutture dati dei singoli TERAPISTI in dizionari annidati (EEG 1-45Hz)

#### Descrizione per codice:

Aiutami a convertire questa struttura dati in un dizionario annidato

**therapists_data_to_dict** è una copia di '**therapists_data**' fatto così

è una **lista di dizionari**
dove per **ogni indice** della lista, ci sono **i dati del singolo soggetto contenuti dentro un dizionario**, che avrà 8 elementi che son **8 chiavi-valore**, 

<br>

**Struttura Originaria**

**therapist_data** = 

[{'**th_1**': {'baseline_1': np.array, 'vision_resp_1': np.array, 'th_resp_1': np.array, 'shared_resp_1'np.array,
           'baseline_1_labels': list, 'vision_resp_1_labels': list, 'th_resp_1_labels': list, 
           'shared_resp_1_labels': list},
{'**th_2**': {'baseline_2': np.array, 'vision_resp_2': np.array, 'th_resp_2': np.array, 'shared_resp_2': np.array,
           'baseline_2_labels': list, 'vision_resp_2_labels': list, 'th_resp_2_labels': list 
           'shared_resp_2_labels': list},
           etc... ]

<br>

quelle **senza '_labels' contengono i dati np.array**, quelle **con '_labels'** contengono **le rispettive etichette, dentro una lista, che vanno convertite in un array numpy** ...

ossia per il primo soggetto, ad esempio, abbiamo che la struttura dati è cpsì

therapists_data[0].keys()
dict_keys(['baseline_1', 'vision_resp_1', 'th_resp_1', 'shared_resp_1', 'baseline_1_labels', 'vision_resp_1_labels', 'th_resp_1_labels', 'shared_resp_1_labels'])

le chiavi con '_labels' son quelle con le labels corrispondenti della chiave che ha la stringa senza '_labels'..

Ora, vorrei per ogni indice della lista (quindi per ogni dizionario associato ad un terapista), vorrei che:

**1)** mi convertissi i valori delle chiavi con labels in delle numpy array 
**2)** mi concatenassi i rispettivi dati e labels con la stessa corrispondenza tra dati e label 

in sintesi vorrei che ci fosse un dizionario annidato che avesse questa struttura

th_data_dict = {'**th_1**': {'data': np.array (i.e., tutti i trials concantenati del soggetto th_1) 
                                            'labels':np.array (i.e., tutte labels dei trials concatenati del soggetto th_1)}

{'**th_2**': {'data': np.array (i.e., tutti i trials concantenati del soggetto th_2) 
                                            'labels':np.array (i.e., tutte labels dei trials concatenati del soggetto th_2)}
<br>


#### Implementazione del codice

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE_1_45/

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/therapists_data.pkl', 'rb') as f:
    therapists_data = pickle.load(f)

In [ ]:
#therapists_data[0]['baseline_1'].shape
#len(therapists_data[0]['baseline_1_labels'][0])

#len(therapists_data[0])
#therapists_data[0].keys()

import copy as cp

therapists_data_to_dict = cp.deepcopy(therapists_data)
#len(therapists_data_to_dict[0])
therapists_data_to_dict[0].keys()

In [ ]:
import numpy as np

# Dizionario finale annidato per tutti i terapisti
th_data_dict = {}

# Iteriamo su ogni soggetto
for idx, therapist_data_dict in enumerate(therapists_data_to_dict):
    
    # Creiamo le liste per accumulare dati e labels
    data_list = []
    labels_list = []

    # Iteriamo su ogni chiave-valore del dizionario del singolo terapista
    for key, value in therapist_data_dict.items():
        if '_labels' in key:
            
            # Convertiamo le labels in np.array e le aggiungiamo alla lista delle labels
            labels_list.append(np.array(value))
        else:
            # Aggiungiamo i dati alla lista dei dati
            data_list.append(value)

    # Concatenazione di tutti i dati e labels per il terapista corrente
    concatenated_data = np.concatenate(data_list, axis=0)
    concatenated_labels = np.concatenate(labels_list, axis=0)

    # Creiamo una chiave unica per il terapista (ad esempio th_1, th_2, ecc.)
    therapist_key = f'th_{idx + 1}'

    # Aggiungiamo al dizionario finale
    th_data_dict[therapist_key] = {
        'data': concatenated_data,
        'labels': concatenated_labels
    }

# Ora th_data_dict conterrà i dati e le labels concatenati per ciascun soggetto
#print(th_data_dict)


In [ ]:
# Iteriamo sul dizionario annidato th_data_dict
for therapist, data_labels in th_data_dict.items():
    print(f"Therapist: \033[1m{therapist}\033[0m")
    
    # Iteriamo su ogni sottochiave (data e labels) del dizionario annidato
    for key, value in data_labels.items():
        print(f"  {key}: {value.shape}")  # Stampiamo la chiave e la shape del valore

In [ ]:
# Dizionario per memorizzare gli indici di inizio e fine delle etichette
labels_indices = {}

# Iteriamo sui soggetti nel dizionario
for therapist_key, data_labels_dict in th_data_dict.items():
    # Estraiamo le labels
    labels = data_labels_dict['labels']
    
    # Dizionario per memorizzare gli indici di ogni etichetta in questo soggetto
    therapist_labels_indices = {}

    # Identifichiamo le etichette uniche
    unique_labels = np.unique(labels)
    
    # Calcoliamo gli indici per ciascuna etichetta
    for label in unique_labels:
        # Troviamo gli indici in cui appare questa etichetta
        label_indices = np.where(labels == label)[0]
        
        # Salviamo l'indice di inizio e fine
        start_idx = label_indices[0]
        end_idx = label_indices[-1]
        
        # Aggiungiamo al dizionario del terapista
        therapist_labels_indices[int(label)] = (start_idx, end_idx)
    
    # Aggiungiamo i risultati per questo terapista
    labels_indices[therapist_key] = therapist_labels_indices

# Stampiamo gli indici
for therapist_key, indices in labels_indices.items():
    print(f"Terapista: \033[1m{therapist_key}\033[0m")
    for label, (start, end) in indices.items():
        print(f"  Etichetta {label}: inizio = {start}, fine = {end}")


In [ ]:
!pwd

In [ ]:
'''PER SALVARE STRUTTURA DATI E LABEL OGNI SOGGETTO NON ANCORA CONCATENATI TRA DI LORO

PS: viene comunque già salvato in  --> new_subject_level_concatenations_th_1_45 '''

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('th_data_dict.pkl', 'wb') as f:
#    pickle.dump(th_data_dict, f) 

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
#path corretta --> cd Plots_Sliding_Estimator_MNE
#path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"

#Comandi da eseguire

#!pwd
#cd Plots_Sliding_Estimator_MNE


import pickle


base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Salva il dizionario th_data_dict in un file pkl
with open(f'{base_path}/new_subject_level_concatenations_th_1_45.pkl', 'wb') as file:
    pickle.dump(th_data_dict, file)

#print("Dati concantenati dei Singoli Terapisti salvati in 'subject_level_concatenations_th_1_45.pkl'")


### STEP 6.1.2.1: Mi concateno le strutture dati e labels dei singoli TERAPISTI (EEG 1-45Hz) INSIEME

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE_1_45

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle
import numpy as np

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_subject_level_concatenations_th_1_45.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_45 = pickle.load(f)

In [ ]:
print(new_subject_level_concatenations_th_1_45.keys())
print()
print(new_subject_level_concatenations_th_1_45['th_1'].keys())
print(np.unique(new_subject_level_concatenations_th_1_45['th_2']['labels'], return_counts = True))

In [ ]:
''' 
                                            OLD APPROACH SBAGLIATO!
import numpy as np

# Crea liste vuote per raccogliere i dati e le labels di tutti i soggetti
all_data = []
all_labels = []

# Itera sui soggetti e aggiungi i dati e le labels alle liste
for subject_key in new_subject_level_concatenations_th_1_45.keys():
    subject_data = new_subject_level_concatenations_th_1_45[subject_key]['data']
    subject_labels = new_subject_level_concatenations_th_1_45[subject_key]['labels']
    
    all_data.append(subject_data)
    all_labels.append(subject_labels)

# Concatena tutti i dati e le labels lungo l'asse 0
concatenated_data = np.vstack(all_data)
concatenated_labels = np.hstack(all_labels)

# Ora concatenated_data e concatenated_labels contengono i dati e le labels di tutti i soggetti concatenati
print("Forma dei dati concatenati:", concatenated_data.shape)
print("Lunghezza delle labels concatenate:", concatenated_labels.shape)

'''



In [ ]:
# Dizionario per raccogliere dati e labels ordinati per etichetta
data_by_label = {}
labels_by_label = {}

# Itera sui soggetti
for subject_key in new_subject_level_concatenations_th_1_45.keys():
    subject_data = new_subject_level_concatenations_th_1_45[subject_key]['data']
    subject_labels = new_subject_level_concatenations_th_1_45[subject_key]['labels']
    
    # Trova le etichette uniche e gli indici corrispondenti
    unique_labels = np.unique(subject_labels)
    
    for label in unique_labels:
        # Trova gli indici dei dati corrispondenti a questa etichetta
        label_indices = np.where(subject_labels == label)[0]
        
        # Estrai i dati e le labels per questi indici
        data_for_label = subject_data[label_indices]
        labels_for_label = subject_labels[label_indices]
        
        # Aggiungi ai dizionari globali, creando la chiave se non esiste
        if label not in data_by_label:
            data_by_label[label] = []
            labels_by_label[label] = []
        
        data_by_label[label].append(data_for_label)
        labels_by_label[label].append(labels_for_label)

# Concatena i dati e le labels per ogni etichetta
concatenated_data_by_label = {}
concatenated_labels_by_label = {}

for label in data_by_label.keys():
    concatenated_data_by_label[label] = np.vstack(data_by_label[label])
    concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
    
    concatenated_data = concatenated_data_by_label[label]
    concatenated_data = concatenated_labels_by_label
    
# Risultato finale: concatenati per etichetta
print("Dati concatenati per etichetta:")
for label in concatenated_data_by_label.keys():
    print(f"Etichetta {label}: {concatenated_data_by_label[label].shape}, {concatenated_labels_by_label[label].shape}")


In [ ]:
# Liste per raccogliere dati e labels di tutte le etichette
all_data = []
all_labels = []

# Itera su tutte le etichette
for label in concatenated_data_by_label.keys():
    all_data.append(concatenated_data_by_label[label])  # Aggiungi i dati concatenati per l'etichetta
    all_labels.append(concatenated_labels_by_label[label])  # Aggiungi le labels concatenate per l'etichetta

# Concatenazione finale
final_data = np.vstack(all_data)  # Concatena tutti i dati
final_labels = np.hstack(all_labels)  # Concatena tutte le labels

# Crea il dizionario finale
new_all_th_concat_reconstructions_1_45 = {
    'data': final_data,
    'labels': final_labels
}

# Controllo delle forme
print(f"Forma finale dei dati: {new_all_th_concat_reconstructions_1_45['data'].shape}")
print(f"Forma finale delle labels: {new_all_th_concat_reconstructions_1_45['labels'].shape}")

In [ ]:
'''VERIFICA CORRETTA LABELS'''

unique_labels, label_counts = np.unique(final_labels, return_counts=True)

# Stampa le etichette uniche e il loro conteggio
print("Etichette uniche e conteggio:", dict(zip(unique_labels, label_counts)))

# Controlla che la somma delle occorrenze corrisponda al numero totale di righe dei dati
print("Totale righe nei dati:", final_data.shape[0])
print("Somma dei conteggi delle etichette:", np.sum(label_counts))

assert final_data.shape[0] == np.sum(label_counts), "Mismatch tra dati e etichette!"


In [ ]:
for label in unique_labels:
    
    # Trova gli indici delle etichette corrispondenti
    label_indices = np.where(final_labels == label)[0]
    
    # Estrai i dati corrispondenti
    data_for_label = final_data[label_indices, :]
    
    # Controlla che la lunghezza corrisponda al conteggio dell'etichetta
    assert data_for_label.shape[0] == label_counts[np.where(unique_labels == label)[0][0]], \
        f"Mismatch per l'etichetta {label}!"
    
    print(f"Etichetta {label} verificata: {data_for_label.shape[0]} dati trovati.")


In [ ]:
# Estrarre le labels dal dizionario
final_labels = new_all_th_concat_reconstructions_1_45['labels']

# Etichette uniche presenti
unique_labels = np.unique(final_labels)

print("Intervalli di indici per ciascuna etichetta:")
# Itera su ciascuna etichetta unica
for label in unique_labels:
    # Trova gli indici corrispondenti a questa etichetta
    label_indices = np.where(final_labels == label)[0]
    
    # Determina l'intervallo
    start_idx = label_indices[0]
    end_idx = label_indices[-1]
    
    # Stampa l'intervallo
    print(f"Etichetta {label}: Indici {start_idx}-{end_idx} (totale: {len(label_indices)})")


In [ ]:
'''SALVO I DATI E LABELS CONCATENATI DI TUTTI I SOGGETTI TERAPISTI PER DATI EEG PREPROCESSED 1-45 Hz'''

import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_1_45, f) 


### STEP 6.2.1.2 - All Single Therapists EEG Preprocessed Data (1-45Hz) across **Couples of Experimental Conditions**

In [ ]:
!pwd

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/therapists_data.pkl', 'rb') as f:
    therapists_data = pickle.load(f)

In [ ]:
therapists_data[0].keys()

In [ ]:
print(f"Baseline in TH_1:, {len(therapists_data[0]['baseline_1_labels'])}\n")
print(f"Th_Resp in TH_1:, {len(therapists_data[0]['th_resp_1_labels'])}\n")
print(f"Pt_Resp in TH_1:, {len(therapists_data[0]['pt_resp_1_labels'])}\n")
print(f"Shared_Resp in TH_1:, {len(therapists_data[0]['shared_resp_1_labels'])}\n")

In [ ]:
'''
DETAILED VERSION WITH PRINTS

Dettagli della struttura finale
Chiavi di primo livello:
Sono i soggetti, ad esempio 'th_1', 'th_2', ..., 'th_16'.

Chiavi di secondo livello:
Sono le combinazioni delle condizioni sperimentali (es. 'baseline_vs_th_resp').

Chiavi di terzo livello:
Ogni combinazione contiene due chiavi: 

'data' (un array concatenato dei dati delle due condizioni) e 
'labels' (un array concatenato delle etichette 0 e 1).

'''

import itertools
import numpy as np


# Condizioni sperimentali
experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']

# Variabile di output
new_subject_level_concatenations_coupled_exp_th_1_45 = {}


# Nuova variabile per tracciare il soggetto corrente stampato
last_subject_key = None

# Dizionario per tenere traccia delle combinazioni già stampate per ogni soggetto
#printed_combinations = {}



# Itera su ogni soggetto nella lista therapists_data
for subject_index, subject_data in enumerate(therapists_data):
    subject_key = f'th_{subject_index + 1}'  # Crea la chiave per il soggetto (es. 'th_1', 'th_2', ...)
    
    
    
    '''PER TRACCIARE SOGGETTO PRECEDENTE'''
    # Aggiungi separazione visiva quando cambia il soggetto
    if subject_key != last_subject_key:
        if last_subject_key is not None:  # Evita di stampare separatori prima del primo soggetto
            print("\n" + "-" * 50 + f" END OF {last_subject_key.upper()} " + "-" * 50 + "\n")
        print(f"\nProcessing Subject: {subject_key}\n" + "=" * 80)
        
        # Inizializza il dizionario delle combinazioni stampate per il nuovo soggetto
        #printed_combinations[subject_key] = set()  # Usando un set per evitare duplicati
    
    last_subject_key = subject_key  # Aggiorna il soggetto corrente
    
    
    # Inizializza il dizionario per questo soggetto
    new_subject_level_concatenations_coupled_exp_th_1_45[subject_key] = {}
    
    '''Creo un suffisso dinamico per 
    1) Estrazione dei dati di una condizione sperimentale di un certo soggetto 
    (i.e., baseline_1 dove "_1" è il suffisso)
    
    2) Estrazione delle labels di una condizione sperimentale di un certo soggetto 
    (i.e., baseline_1_labels dove "_1_labels" è il suffisso)
    '''
    
    # Suffisso dinamico basato sull'indice del soggetto
    data_suffix = f"_{subject_index + 1}"
    labels_suffix = f"{data_suffix}_labels"
    
    # Crea tutte le combinazioni uniche di condizioni sperimentali
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
    
    # Loop su tutte le combinazioni di condizioni
    for cond_1, cond_2 in condition_pairs:
        condition_pair_key = f"{cond_1}_vs_{cond_2}"  # Nome della combinazione (es. 'baseline_vs_th_resp')
        
        
        # Controlla se la combinazione è già stata stampata per il soggetto corrente
        #if condition_pair_key in printed_combinations[subject_key]:
        #    continue  # Salta la combinazione se è già stata stampata
        
        # Stampa il messaggio per la prima volta che incontriamo questa combinazione
        print(f"\n\t\tCreation of Coupled Condition \033[1m{condition_pair_key}\033[0m")
        
        # Aggiungi la combinazione al set delle combinazioni stampate per il soggetto
        #printed_combinations[subject_key].add(condition_pair_key)
        
        #print(condition_pair_key
                    
        #Estrai i dati e le etichette per le due condizioni
        data_cond_1 = subject_data.get(f"{cond_1}{data_suffix}")
        print(f"Extracting data_cond_1 which is {cond_1}{data_suffix}")
        labels_cond_1 = subject_data.get(f"{cond_1}{labels_suffix}")
        print(f"Extracting labels_cond_1 which is {cond_1}{labels_suffix}")
        
        data_cond_2 = subject_data.get(f"{cond_2}{data_suffix}")
        labels_cond_2 = subject_data.get(f"{cond_2}{labels_suffix}")
        
        # Verifica che i dati e le etichette siano validi
        if data_cond_1 is None or labels_cond_1 is None or data_cond_2 is None or labels_cond_2 is None:
            continue  # Salta se manca qualcosa
        
        # Converti le etichette da lista a numpy array
        labels_cond_1 = np.zeros(len(labels_cond_1), dtype=int)  # Etichette di cond_1 come 0
        labels_cond_2 = np.ones(len(labels_cond_2), dtype=int)   # Etichette di cond_2 come 1
        
        # Concatenazione dei dati e delle etichette
        concatenated_data = np.vstack((data_cond_1, data_cond_2))
        concatenated_labels = np.hstack((labels_cond_1, labels_cond_2))
        
        # Salva i dati concatenati nella struttura
        new_subject_level_concatenations_coupled_exp_th_1_45[subject_key][condition_pair_key] = {
            'data': concatenated_data,
            'labels': concatenated_labels
        }
        
        # Dopo aver trattato tutti i livelli, aggiungi una separazione visiva per il soggetto
        print("-" * 50 + f"-" * 50)


In [ ]:
#new_subject_level_concatenations_coupled_exp_th_1_45.keys()
#new_subject_level_concatenations_coupled_exp_th_1_45['th_1'].keys()
#new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp'].keys()
print(f"Data Shape: {new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp']['data'].shape}")
print()
print(f"Data Shape: {new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp']['labels'].shape}")
print()
print(f"Counts Shape: {np.unique(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp']['labels'], return_counts = True)}")

In [ ]:
print(f"\t\t\t\t\033[1mStructure of new_subject_level_concatenations_coupled_exp_th_1_20\033[0m: \n")
print(f"\033[1mFirst Order Keys\033[0m: {new_subject_level_concatenations_coupled_exp_th_1_45.keys()}\n")
print(f"\033[1mSecond Order Keys\033[0m: {new_subject_level_concatenations_coupled_exp_th_1_45['th_1'].keys()}\n")
print(f"\033[1mThird Order Keys\033[0m: \n{new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp'].keys()}\n")

In [ ]:
'''VERIFICO CHE LA CONCATENAZIONE SIA AVVENUTA CORRETTAMENTE!'''

print("\tNOW, LET US SEE IF THE CONCATENATIONS RESPECT THE ORIGINAL SHAPES FOR EVERY COUPLED EXPERIMENTAL CONDITION!")
print("\tFOR THE 1°ST SUBJECT: CHECK IF THE SUM OF INDIVIDUAL EXP COND SHAPE MATCHES THE COUPLED COND CONCATENATION SHAPE:\n\n")

print("\033[1mINDIVIDUAL EXP COND SHAPE OF FIRST SUBJECT\033[0m:")


print(f"Baseline in TH_1: {len(therapists_data[0]['baseline_1_labels'])}\n")
print(f"Th_Resp in TH_1: {len(therapists_data[0]['th_resp_1_labels'])}\n")
print(f"Pt_Resp in TH_1: {len(therapists_data[0]['pt_resp_1_labels'])}\n")
print(f"Shared_Resp in TH_1: {len(therapists_data[0]['shared_resp_1_labels'])}\n")
print()

#new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp']['data'].shape
#new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp']['labels'].shape

# Seleziona il primo soggetto (ad esempio, 'th_1')
subject_key = 'th_1'


# Itera per il soggetto
for condition_pair_key, pair_data in new_subject_level_concatenations_coupled_exp_th_1_45[subject_key].items():
 
    # Estrai i dati e le etichette per ogni coppia di condizioni
    data = pair_data.get('data')
    labels = pair_data.get('labels')

    # Stampa il nome della coppia di condizioni e le loro dimensioni
    print(f"Condition Pair: \033[1m{condition_pair_key}\033[0m")

    if data is not None and labels is not None:
        print(f"  Data Shape: {data.shape}")
        print(f"  Labels Shape: {labels.shape}")
    else:
        print("  Missing data or labels!")

In [ ]:
print(np.unique(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp']['labels'], return_counts = True))
print(np.unique(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['th_resp_vs_shared_resp']['labels'], return_counts = True))

In [ ]:
print(f"\t\t\t\033[1mBASELINE_VS_TH_RESP\033[0m")
print(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp']['labels'][:44])
print()
print(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp']['labels'][44:])
print()
print(f"\t\t\t\033[1mTH_RESP_VS_SHARED_RESP\033[0m")
print(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['th_resp_vs_shared_resp']['labels'][:40])
print()
print(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['th_resp_vs_shared_resp']['labels'][40:])

#### STEP 6.2.1.3 - Salvataggio Dataset di All Single Therapists EEG Preprocessed Data (1-45Hz) across Couples of Experimental Conditions

In [ ]:
!pwd

In [ ]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_1_45'''

import pickle
   
base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_subject_level_concatenations_coupled_exp_th_1_45.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_coupled_exp_th_1_45, f)

### STEP 6.2.2 Mi concanteno All Single Therapists EEG Preprocessed Data (1-45Hz) across **Couples of Experimental Conditions**

#### Istruzioni

Perfetto, ora vorrei che, nel prossimo codice che vorrei mi aiutassi a creare, dovresti fare la stessa cosa, ma per una struttura con un livello in più che avrebbe ad esempio questa struttura..


print(new_subject_level_concatenations_coupled_exp_th_1_45.keys())
print()
print(new_subject_level_concatenations_coupled_exp_th_1_45['th_1'].keys())
print(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp'].keys())
print(np.unique(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp']['labels'], return_counts = True))

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16', 'th_17', 'th_18', 'th_19', 'th_20'])

dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])
dict_keys(['data', 'labels'])
(array([0, 1]), array([44, 40]))

ogni condizione sperimentale ('baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp') avrebbe i dati e labels in sostanza associati alla coppia di condizioni sperimentali, dove, la prima stringa della chiave della condizione sperimentale corrisponde alle etichette 0, e l'altra 1.

ora, io vorrei che, per ogni soggetto, 

1) tu identifichi la specifica chiave associata alla stessa condizione sperimetnale,

2) entri dentro quella chiave e prendi i dati e le labels di ogni soggetto e li concateni uno sotto l'altro, come prima.

3) vorrei avere, alla fine, che si creassero una serie di nuovi dizionari, che si chiameranno similarmente. 

nello specifico avranno un prefisso, un termine dinamico ed un suffisso...

- il prefisso sarà "new_all_th_concat_reconstructions_" 

-il termine dinamico cambierà, a seconda della condizione sperimentale iterata in quel momento, che sarebbe tra quelle condizioni sperimentali iterate ('baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp') 

-il suffisso, che sarebbe "_1_45"..

in sostanza dovrebbe apparire una cosa del genere :

"new_all_th_concat_reconstructions_{condition_pair}_1_45"

alla fine, dovrei avere, se non sbaglio, 6 dizionari, ciascuno che conterrà il set di dati e labels di tutti i terapisti per tutte le combinazioni possibili di coppie di condizioni sperimentali.

ti è chiaro cosa vorrei che facessi ora?

<br>


**CHAT**

Sì, mi è chiaro cosa vuoi fare. Ecco un riassunto dei passaggi:

Iterare su ciascuna condizione sperimentale: Ogni chiave della struttura new_subject_level_concatenations_coupled_exp_th_1_45['th_1'] rappresenta una condizione sperimentale (es. 'baseline_vs_th_resp', ecc.).

Concatenare i dati e le etichette: Per ogni condizione sperimentale, estrarre i dati ('data') e le etichette ('labels') di tutti i soggetti e concatenarli.

Creare dizionari per ogni condizione sperimentale: Creare un dizionario con il nome dinamico basato sulla condizione sperimentale, come "new_all_th_concat_reconstructions_{condition_pair}_1_45", contenente i dati concatenati e le etichette concatenate.



**IO**

Per fare questo in maniera più elegante, crea una funzione, che ritorna in un dizionario tutti e 6 i sotto-dizionari nuovi, ciascuno che conterrà il set di dati e labels di tutti i terapisti per tutte le combinazioni possibili di coppie di condizioni sperimentali! 


#### Implementazione 

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle
import numpy as np

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_subject_level_concatenations_coupled_exp_th_1_45.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th_1_45 = pickle.load(f)

In [ ]:
print(new_subject_level_concatenations_coupled_exp_th_1_45.keys())
print()
print(new_subject_level_concatenations_coupled_exp_th_1_45['th_1'].keys())
print(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp'].keys())
print(np.unique(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp']['labels'], return_counts = True))

In [ ]:
def concatenate_all_single_subj_coupled_experimental_conditions_th(data_structure, conditions, prefix, suffix):
    
    """
    Concatena i dati e le etichette per ogni condizione sperimentale da una struttura dati con un livello in più,
    dove questo livello rappresenta le diverse coppie di condizioni sperimentali iterate nel ciclo ossia
    
    'baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 
    'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'
    
    ordinandoli anche per etichetta.
    
    Questo perché ogni array di labels avrà sempre o 0 od 1 come etichette,
    dato che son coppie di condizioni sperimentali

    Parameters:
        data_structure (dict): La struttura dati di input che contiene i dati per soggetti e condizioni.
        conditions (list): Le condizioni sperimentali (chiavi del secondo livello) da processare.
        prefix (str): Il prefisso del nome dinamico del dizionario.
        suffix (str): Il suffisso del nome dinamico del dizionario.

    Returns:
        dict: Un dizionario contenente i nuovi dizionari con i dati concatenati e le etichette per ogni coppia di condizioni sperimentali
    """
    
    #Questo conterrà i dati complessivi di tutti i soggetti per ogni coppia di condizioni sperimentali
    all_subj_data_by_coupled_cond = {}

    # Itera su ogni condizione sperimentale
    for condition_pair in conditions:
        
        # Dizionari per raccogliere dati e labels ordinati per ogni coppia di condizioni sperimentali
        # che è dinamico, per ogni coppia di condizioni sperimentali 
        
        #(quindi si ricreeranno passando alla condizione sperimentale successiva!)
        
        data_by_label = {}
        labels_by_label = {}
        
        
        # Lista temporanea per salvare la shape delle etichette per ogni soggetto per ogni etichetta iterata
        
        '''
        Per ogni condizione sperimentale, per ognuna delle 2 labels, 
        la shape delle etichette per ogni soggetto, 

        e me le salvi dentro una lista temporanea, che salva in formato la shape (solo il valore numerico) di ogni soggetto 
        per l'etichette iterata per quella condizione sperimentale là.

        poi, a questo livello dei print 

         # **Print finale per verificare la concatenazione per ogni label**
            print(f"Condizione: {condition_pair}, Etichetta: {label}")
            print(f"  - Shape dei dati concatenati per {label}: {concatenated_data_by_label[label].shape}")
            print(f"  - Shape delle etichette concatenate per {label}: {concatenated_labels_by_label[label].shape}")

        vorrei che mi stampassi anche questa lista alla fine del print, 
        di modo che possa vedere visivamente subito il numero di labels di ogni soggetto associate 
        a quella labels iterata là, 
        così da vedere se il conteggio corrisponde visivamente al totale salvate dentro 

        "concatenated_data_by_label[label]"
        '''
        
        shape_labels_per_subject = {0: [], 1: []}  # Inizializza un dizionario per le etichette 0 e 1


        # Itera su tutti i soggetti
        # In questo caso, itera sulle chiavi di ogni soggetto
        
        # Quindi prenderà, per la relativa coppia di condizioni sperimentali di ogni soggetto,
        # i dati e le labels di quel soggetto, per quella relativa coppia di condizioni sperimentali
        
        for subject_key in data_structure.keys():
            
            
            # Qui estrae i dati e le labels per questa condizione sperimentale di quel soggettio lì
            subject_data = data_structure[subject_key][condition_pair]['data']
            subject_labels = data_structure[subject_key][condition_pair]['labels']

            # Trova le etichette uniche e gli indici corrispondenti per quella coppia di condizioni sperimentali lì,
            # Ossia, potrà trovare gli 0 e gli 1 
            
            unique_labels = np.unique(subject_labels)
        
            #A quel punto, per ognuna delle due labels trovate per quella coppia di condizioni sperimentali lì
            #Che saranno sempre o 0 o 1
            
            for label in unique_labels:
                
                # Trova gli indici dei dati corrispondenti a questa etichetta
                # Una volta per lo 0 ed una volta per l' 1
                
                label_indices = np.where(subject_labels == label)[0]

                # A quel punto, estrae i dati e le labels per questi indici
                # Una volta per lo 0 ed una volta per l' 1
                
                data_for_label = subject_data[label_indices]
                labels_for_label = subject_labels[label_indices]

                # A quel punto, per ogni soggetto, per ogni condzione sperimentale, 
                # per quelle due labels là (sempre presenti, per ogni coppia di condizioni sperimentali)
                # Una volta per lo 0 ed una volta per l' 1
                
                #Andrà a creare per ogni etichetta, una chiave che si chiamerà 
                #o 0 od 1 (inizialmente, vuoto -> perché deve esser inizializzato)
                #E poi, dopo, ci appenderà le labels 
                 # Una volta per lo 0 ed una volta per l' 1
                #  Di quel soggetto per quella coppia di condizioni sperimentali iterate a quel momento
                
                #Aggiunge ai dizionari globali, creando la chiave se non esiste
                if label not in data_by_label:
                    data_by_label[label] = []
                    labels_by_label[label] = []

                data_by_label[label].append(data_for_label)
                labels_by_label[label].append(labels_for_label)
                
                 # **Salva la shape delle etichette per il soggetto corrente**
                shape_labels_per_subject[label].append(labels_for_label.shape[0])  # Aggiungi solo la dimensione (numero di etichette)

        
                # **Aggiungi un print di controllo per ogni soggetto**
                print(f"Soggetto: \033[1m{subject_key}\033[0m, Condizione: \033[1m{condition_pair}\033[0m, Etichetta: \033[1m{label}\033[0m, Shape: \033[1m{labels_for_label.shape[0]}\033[0m")
                #print(f"  - Numero di \033[1mdati\033[0m per {label}: {data_for_label.shape[0]}")
                #print(f"  - Numero di \033[1metichette\033[0m per {label}: {labels_for_label.shape[0]}")
                
                    
        # Dopodiché, vado a creare invece i dizionari che conterranno
        # Le concatenazioni, di dati e labels corrispondenti, di tutti i soggetti per cui l'etichetta era 
        # o 0 od 1 
        
        # Di conseguenza, qui dentro dovrei avere, per ogni coppia di condizioni sperimentali
        # Tutti gli 0 ed 1 (ed i relativi dati corrispondenti)
        # di tutti i soggetti, ma concatenati
        
        
        concatenated_data_by_label = {}
        concatenated_labels_by_label = {}

        for label in data_by_label.keys():
            concatenated_data_by_label[label] = np.vstack(data_by_label[label])
            concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
            
            # **Calcolare la shape totale delle etichette**
            #total_labels_0 = np.sum(1 for subject_labels in labels_by_label[label] if 0 in subject_labels)
            #total_labels_1 = np.sum(1 for subject_labels in labels_by_label[label] if 1 in subject_labels)
            #total_labels = total_labels_0 + total_labels_1

            # **Determinare gli indici delle etichette 0 e 1 nell'array finale**
            
            # Gli indici delle etichette 0
            indices_labels_0 = np.where(concatenated_labels_by_label[label] == 0)[0]
            
            # Gli indici delle etichette 1
            indices_labels_1 = np.where(concatenated_labels_by_label[label] == 1)[0]
            
            # Indici iniziale e finale per le etichette 0 e 1
            start_idx_0 = indices_labels_0[0] if len(indices_labels_0) > 0 else None
            end_idx_0 = indices_labels_0[-1] if len(indices_labels_0) > 0 else None
            start_idx_1 = indices_labels_1[0] if len(indices_labels_1) > 0 else None
            end_idx_1 = indices_labels_1[-1] if len(indices_labels_1) > 0 else None
    
    
            # **Print finale per verificare la concatenazione per ogni label**
            #print(f"\nCondizione: \033[1m{condition_pair}\033[0m, Etichetta: {label}")
            #print(f"  - Shape dei dati concatenati per \033[1m{label}\033[0m: {concatenated_data_by_label[label].shape}")
            #print(f"  - Shape delle etichette concatenate per \033[1m{label}\033[0m: {concatenated_labels_by_label[label].shape}")
            
            # **Stampa la lista delle shapes delle etichette per ogni soggetto per questa etichetta**
            #print(f"\n  - Shape delle etichette per soggetto (per etichetta {label}): {shape_labels_per_subject[label]}\n")

            
            # **Stampa il conteggio totale delle etichette**
            #print(f"\n  - Totale delle etichette 0: {total_labels_0}")
            #print(f"  - Totale delle etichette 1: {total_labels_1}")
            #print(f"  - Totale delle etichette per la condizione: {total_labels}\n")

            # **Stampa gli indici per le etichette 0 e 1**
            # **OSSIA --> Stampa gli indici per l'etichetta corrente**
            
            #if label == 0:
            #    print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #else:
            #    print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}\n")

    
            #print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}")

    
        #ARRIVATI FINO A QUI, abbiamo che siccome stiamo iterando prima per tutti gli 0 e poi per tutti gli 1
        #Significa che, assumendo che siamo dentro 'baseline_vs_th_resp' e che 
        
        #'baseline' sia rappresentato dalle etichette 0
        #'th_resp' sia rappresentato dalle etichette 1
        
        #Al PRIMO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'baseline' per 'baseline_vs_th_resp'di tutti i soggetti)
        
        #Al SECONDO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #Quindi mi manca ancora 
        
        #A) CONCATENARE I DATI:
        
        #1)prima tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        
        #che verrà fatto dentro all_data (che è anch'esso una variabile dinamica!)
        
        #B) CONCATENARE LE LABELS:
        
        #1)prima tutti le labels (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti le labels (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #che verrà fatto dentro all_labels (che è anch'esso una variabile dinamica!)
        
        # Liste per raccogliere dati e labels di tutte le etichette
        
        # Qui dentro, invece, dov con
        all_data = []
        all_labels = []

        for label in concatenated_data_by_label.keys():
            all_data.append(concatenated_data_by_label[label])
            all_labels.append(concatenated_labels_by_label[label])
        
        
        #Alla fine, qui dentro avrò che, PER OGNI COPPIA DI CONDIZIONI SPERIMENTALI
        
        
        #'final_data' dovrebbe avere 
            #- prima tutti i dati di tutti i soggetti associati all'etichetta 0 
            #- e poi tutti i dati di tutti i soggetti associati all'etichetta 1
        
        #'final_labels' dovrebbe avere 
            #- prima tutte le labels di tutti i soggetti associati all'etichetta 0
            #- e poi tutte tutte le labels di tutti soggetti associati all'etichetta 1...

        
        # Concatenazione finale per la condizione corrente
        final_data = np.vstack(all_data)
        final_labels = np.hstack(all_labels)
    
        
        # Nome dinamico del dizionario
        dict_name = f"{prefix}{condition_pair}{suffix}"

        # Salva il risultato nel dizionario globale
        all_subj_data_by_coupled_cond[dict_name] = {
            'data': final_data,
            'labels': final_labels
        }
        
    # Dopo aver costruito tutti i sotto-dizionari, iterare per stampare gli intervalli
    print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")

    for cond_key, cond_data in all_subj_data_by_coupled_cond.items():
        print(f"Condizione: \033[1m{cond_key}\033[0m\n")

        # Estrai le etichette dal sotto-dizionario
        labels = cond_data['labels']

        # Conta le etichette uniche
        unique_labels = np.unique(labels)

        # Variabile per il conteggio totale delle etichette
        total_labels = 0

        # Stampa gli intervalli di indici per ciascuna etichetta
        for label in unique_labels:

            # Trova gli indici corrispondenti a questa etichetta
            label_indices = np.where(labels == label)[0]

            # Determina l'intervallo
            start_idx = label_indices[0]
            end_idx = label_indices[-1]

            # Aggiungi il numero di occorrenze al conteggio totale
            total_labels += len(label_indices)

            # Stampa l'intervallo
            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m (Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

        # Stampa il totale delle etichette per la condizione corrente
        print(f"\nTotale etichette (0 e 1): \033[1m{total_labels}\033[0m\n")

    return all_subj_data_by_coupled_cond


In [ ]:
# Parametri
conditions = ['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp',
              'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp']

prefix = "new_all_th_concat_reconstructions_"
suffix = "_1_45"

# Chiamata alla funzione
new_concatenated_dictionaries = concatenate_all_single_subj_coupled_experimental_conditions_th(
    data_structure=new_subject_level_concatenations_coupled_exp_th_1_45,
    conditions=conditions,
    prefix=prefix,
    suffix=suffix
)

# Stampa i risultati per verifica
print('\n\033[1mRISULTATO FINALE TUTTI I SOGGETTI TH\033[0m') 
for key, value in new_concatenated_dictionaries.items():
    print(f"{key}:")
    print(f"  Dati: {value['data'].shape}")
    print(f"  Labels: {value['labels'].shape}")


#### STEP 6.2.2.1 - Salvataggio Dataset di **All Single Therapists** EEG Preprocessed Data (1-45Hz) across **Couples of Experimental Conditions** INSIEME

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE_1_45

In [ ]:
new_concatenated_dictionaries.keys()

In [ ]:
#Mi estraggo ogni sotto-dizionario

new_all_th_concat_reconstructions_baseline_vs_th_resp_1_45 = new_concatenated_dictionaries['new_all_th_concat_reconstructions_baseline_vs_th_resp_1_45']

new_all_th_concat_reconstructions_baseline_vs_pt_resp_1_45 = new_concatenated_dictionaries['new_all_th_concat_reconstructions_baseline_vs_pt_resp_1_45']

new_all_th_concat_reconstructions_baseline_vs_shared_resp_1_45 = new_concatenated_dictionaries['new_all_th_concat_reconstructions_baseline_vs_shared_resp_1_45']

new_all_th_concat_reconstructions_th_resp_vs_pt_resp_1_45 = new_concatenated_dictionaries['new_all_th_concat_reconstructions_th_resp_vs_pt_resp_1_45']
        
new_all_th_concat_reconstructions_th_resp_vs_shared_resp_1_45 = new_concatenated_dictionaries['new_all_th_concat_reconstructions_th_resp_vs_shared_resp_1_45']

new_all_th_concat_reconstructions_pt_resp_vs_shared_resp_1_45 = new_concatenated_dictionaries['new_all_th_concat_reconstructions_pt_resp_vs_shared_resp_1_45']

In [ ]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_NF '''
import pickle
   
base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#'BASELINE VS TH RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_baseline_vs_th_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_baseline_vs_th_resp_1_45, f)
                                  
#'BASELINE VS PT RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_baseline_vs_pt_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_baseline_vs_pt_resp_1_45, f)
        
#'BASELINE VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_baseline_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_baseline_vs_shared_resp_1_45, f)
    
#'TH RESP VS PT RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_th_resp_vs_pt_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_th_resp_vs_pt_resp_1_45, f)
        
#'TH RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_th_resp_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_th_resp_vs_shared_resp_1_45, f)
    
#'PT RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_pt_resp_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_pt_resp_vs_shared_resp_1_45, f)
    

### STEP 6.2.3 - All Single Therapists EEG Preprocessed Data (1-45Hz) across **Triplets of Experimental Conditions**

#### Procedura

Per calcolare quante possibili triplette (combinazioni di 3 condizioni sperimentali) si possono formare da un insieme di 4 condizioni, utilizziamo il concetto di combinazioni senza ripetizione. La formula per il numero di combinazioni è:

C(n,k)=  k!⋅(n−k)! / n!

Dove:

- n è il numero totale di elementi nell'insieme (n = 4 in questo caso)
- k è il numero di elementi scelti (k = 3)


**Calcoliamo**:

C(4,3)= 4!/ 3⋅(4−3)! = 4⋅3⋅2⋅1 / (3⋅2⋅1)⋅1 = 4 

**Risultato**

Ci sono 4 possibili triplette che si possono formare dalle 4 condizioni sperimentali.

**Elenco delle Triplette**

Se vogliamo enumerarle:

['baseline', 'th_resp', 'pt_resp']
['baseline', 'th_resp', 'shared_resp']
['baseline', 'pt_resp', 'shared_resp']
['th_resp', 'pt_resp', 'shared_resp']

Queste sono tutte le combinazioni possibili

#### Implementazione

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE_1_45/

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/therapists_data.pkl', 'rb') as f:
    therapists_data = pickle.load(f)

In [ ]:
import itertools
import numpy as np

# Condizioni sperimentali
experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']

# Variabile di output
new_subject_level_concatenations_triplets_exp_th_1_45 = {}

# Nuova variabile per tracciare il soggetto corrente stampato
last_subject_key = None

# Itera su ogni soggetto nella lista therapists_data
for subject_index, subject_data in enumerate(therapists_data):
    subject_key = f'th_{subject_index + 1}'  # Crea la chiave per il soggetto (es. 'th_1', 'th_2', ...)

    '''PER TRACCIARE SOGGETTO PRECEDENTE'''
    # Aggiungi separazione visiva quando cambia il soggetto
    if subject_key != last_subject_key:
        if last_subject_key is not None:  # Evita di stampare separatori prima del primo soggetto
            print("\n" + "-" * 50 + f" END OF {last_subject_key.upper()} " + "-" * 50 + "\n")
        print(f"\nProcessing Subject: {subject_key}\n" + "=" * 80)

    last_subject_key = subject_key  # Aggiorna il soggetto corrente

    # Inizializza il dizionario per questo soggetto
    new_subject_level_concatenations_triplets_exp_th_1_45[subject_key] = {}

    '''Creo un suffisso dinamico per:
    1) Estrazione dei dati di una condizione sperimentale di un certo soggetto 
    (i.e., baseline_1 dove "_1" è il suffisso)
    2) Estrazione delle labels di una condizione sperimentale di un certo soggetto 
    (i.e., baseline_1_labels dove "_1_labels" è il suffisso)
    '''
    # Suffisso dinamico basato sull'indice del soggetto
    data_suffix = f"_{subject_index + 1}"
    labels_suffix = f"{data_suffix}_labels"

    # Crea tutte le combinazioni uniche di triplette di condizioni sperimentali
    condition_triplets = list(itertools.combinations(experimental_conditions, 3))

    # Loop su tutte le combinazioni di triplette
    for cond_1, cond_2, cond_3 in condition_triplets:
        condition_triplet_key = f"{cond_1}_vs_{cond_2}_vs_{cond_3}"  # Nome della combinazione

        # Stampa il messaggio per la triplette corrente
        print(f"\n\t\tCreation of Triplet Condition \033[1m{condition_triplet_key}\033[0m")

        # Estrai i dati e le etichette per le tre condizioni
        data_cond_1 = subject_data.get(f"{cond_1}{data_suffix}")
        print(f"Extracting data_cond_1 which is {cond_1}{data_suffix}")
        labels_cond_1 = subject_data.get(f"{cond_1}{labels_suffix}")
        print(f"Extracting labels_cond_1 which is {cond_1}{labels_suffix}")

        data_cond_2 = subject_data.get(f"{cond_2}{data_suffix}")
        print(f"Extracting data_cond_1 which is {cond_2}{data_suffix}")
        labels_cond_2 = subject_data.get(f"{cond_2}{labels_suffix}")
        print(f"Extracting labels_cond_1 which is {cond_2}{labels_suffix}")

        data_cond_3 = subject_data.get(f"{cond_3}{data_suffix}")
        print(f"Extracting data_cond_1 which is {cond_3}{data_suffix}")
        labels_cond_3 = subject_data.get(f"{cond_3}{labels_suffix}")
        print(f"Extracting labels_cond_1 which is {cond_3}{labels_suffix}")
        
        # Verifica che i dati e le etichette siano validi
        #if any(x is None for x in [data_cond_1, labels_cond_1, data_cond_2, labels_cond_2, data_cond_3, labels_cond_3]):
        #    print(f'PROBLEM FOR THE SUBJECT {subject_index}')  
        #else: 
        #    continue # Salta se manca qualcosa

        # Converti le etichette da lista a numpy array con valori univoci per ciascuna condizione
        labels_cond_1 = np.zeros(len(labels_cond_1), dtype=int)  # Etichette di cond_1 come 0
        labels_cond_2 = np.ones(len(labels_cond_2), dtype=int)   # Etichette di cond_2 come 1
        labels_cond_3 = np.full(len(labels_cond_3), 2, dtype=int)  # Etichette di cond_3 come 2

        # Concatenazione dei dati e delle etichette
        concatenated_data = np.vstack((data_cond_1, data_cond_2, data_cond_3))
        concatenated_labels = np.hstack((labels_cond_1, labels_cond_2, labels_cond_3))

        # Salva i dati concatenati nella struttura
        new_subject_level_concatenations_triplets_exp_th_1_45[subject_key][condition_triplet_key] = {
            'data': concatenated_data,
            'labels': concatenated_labels
        }

        # Dopo aver trattato tutti i livelli, aggiungi una separazione visiva per il soggetto
        print("-" * 50 + f"-" * 50)

        

In [ ]:
# Itera su ogni soggetto nel dizionario delle triplette
print("\n\033[1mIndicizzazione dei dati e delle etichette per ogni sotto-tripletta di condizioni sperimentali:\033[0m\n")

for subject_key, triplets_data in new_subject_level_concatenations_triplets_exp_th_1_45.items():
    print(f"\nSoggetto: \033[1m{subject_key}\033[0m")
    print("=" * 80)

    for triplet_key, triplet_data in triplets_data.items():
        print(f"\nTripletta: \033[1m{triplet_key}\033[0m")
        
        # Estrai i dati e le etichette
        concatenated_data = triplet_data['data']
        concatenated_labels = triplet_data['labels']
        
        # Conta le etichette uniche
        unique_labels = np.unique(concatenated_labels)
        
        # Variabile per il conteggio totale
        total_samples = 0
        
        for label in unique_labels:
            # Trova gli indici corrispondenti a questa etichetta
            label_indices = np.where(concatenated_labels == label)[0]
            
            # Determina l'intervallo di indici
            start_idx = label_indices[0]
            end_idx = label_indices[-1]
            
            # Aggiungi il numero di campioni al totale
            total_samples += len(label_indices)
            
            # Stampa le informazioni sull'etichetta
            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m (Totale: {len(label_indices)})")
        
        # Verifica il totale dei campioni
        print(f"\nTotale campioni: \033[1m{total_samples}\033[0m")
        print("-" * 80)

In [ ]:
!pwd

In [ ]:
'''PER SALVARE STRUTTURA DATI E LABEL OGNI SOGGETTO NON ANCORA CONCATENATI TRA DI LORO

PS: viene comunque già salvato in  --> new_subject_level_concatenations_triplets_exp_th_1_45 '''

import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Salva il dizionario th_data_dict in un file pkl
with open(f'{base_path}/new_subject_level_concatenations_triplets_exp_th_1_45.pkl', 'wb') as file:
    pickle.dump(new_subject_level_concatenations_triplets_exp_th_1_45, file)


### STEP 6.2.3.1 - Mi concanteno All Single Therapists EEG Preprocessed Data (1-45Hz) across **Triplets of Experimental Conditions**

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_subject_level_concatenations_triplets_exp_th_1_45.pkl', 'rb') as f:
    new_subject_level_concatenations_triplets_exp_th_1_45 = pickle.load(f)

In [ ]:
#new_subject_level_concatenations_triplets_exp_th_1_45.keys()
new_subject_level_concatenations_triplets_exp_th_1_45['th_1'].keys()

In [ ]:
new_subject_level_concatenations_triplets_exp_th_1_45['th_1']['baseline_vs_th_resp_vs_pt_resp'].keys()

In [ ]:
# Itera attraverso ogni soggetto nel dizionario
for i, subject_data in new_subject_level_concatenations_triplets_exp_th_1_45.items():
    print(f"Soggetto {i}:")
    print("Chiavi presenti:", list(subject_data.keys()))
    print("-" * 50)

In [ ]:

def concatenate_all_single_subj_tripled_experimental_conditions_th(data_structure, conditions, prefix, suffix):
    
    """
    Concatena i dati e le etichette per ogni condizione sperimentale da una struttura dati con un livello in più,
    ordinandoli anche per etichetta.

    Parameters:
        data_structure (dict): La struttura dati di input che contiene i dati per soggetti e condizioni.
        conditions (list): Le condizioni sperimentali (chiavi del secondo livello) da processare.
        prefix (str): Il prefisso del nome dinamico del dizionario.
        suffix (str): Il suffisso del nome dinamico del dizionario.

    Returns:
        dict: Un dizionario contenente i nuovi dizionari con i dati concatenati e le etichette per ogni condizione.
    """
    
    #Questo conterrà i dati complessivi di tutti i soggetti per ogni coppia di condizioni sperimentali
    all_subj_data_by_coupled_cond = {}

    # Itera su ogni condizione sperimentale
    for condition_triplet in conditions:
        
        # Dizionari per raccogliere dati e labels ordinati per ogni coppia di condizioni sperimentali
        # che è dinamico, per ogni coppia di condizioni sperimentali 
        
        #(quindi si ricreeranno passando alla condizione sperimentale successiva!)
        
        
        #print(f"Creo dizionari di dati e labels per la condizione:")
        #print(f"\n{condition_triplet}")
        data_by_label = {}
        labels_by_label = {}
        
        
        # Lista temporanea per salvare la shape delle etichette per ogni soggetto per ogni etichetta iterata
        
        '''
        Per ogni condizione sperimentale, per ognuna delle 2 labels, 
        la shape delle etichette per ogni soggetto, 

        e me le salvi dentro una lista temporanea, che salva in formato la shape (solo il valore numerico) di ogni soggetto 
        per l'etichette iterata per quella condizione sperimentale là.

        poi, a questo livello dei print 

         # **Print finale per verificare la concatenazione per ogni label**
            print(f"Condizione: {condition_triplet}, Etichetta: {label}")
            print(f"  - Shape dei dati concatenati per {label}: {concatenated_data_by_label[label].shape}")
            print(f"  - Shape delle etichette concatenate per {label}: {concatenated_labels_by_label[label].shape}")

        vorrei che mi stampassi anche questa lista alla fine del print, di modo che possa vedere visivamente subito il numero di labels di ogni soggetto associate a quella labels iterata là così da vedere se il conteggio corrisponde visivamente al totale salvate dentro 

        "concatenated_data_by_label[label]"
        '''
        
        shape_labels_per_subject = {0: [], 1: [], 2: []}  # Inizializza un dizionario per le etichette 0 e 1


        # Itera su tutti i soggetti
        # In questo caso, itera sulle chiavi di ogni soggetto
        
        # Quindi prenderà, per la relativa coppia di condizioni sperimentali di ogni soggetto,
        # i dati e le labels di quel soggetto, per quella relativa coppia di condizioni sperimentali
        
        for subject_key in data_structure.keys():
            
            #print(subject_key)
            #print(data_structure.keys())
            
            # Qui estrae i dati e le labels per questa condizione sperimentale di quel soggettio lì
            subject_data = data_structure[subject_key][condition_triplet]['data']
            subject_labels = data_structure[subject_key][condition_triplet]['labels']

            # Trova le etichette uniche e gli indici corrispondenti per quella coppia di condizioni sperimentali lì,
            # Ossia, potrà trovare gli 0 e gli 1 
            
            unique_labels = np.unique(subject_labels)
        
            #A quel punto, per ognuna delle due labels trovate per quella coppia di condizioni sperimentali lì
            #Che saranno sempre o 0 o 1 
            
            for label in unique_labels:
                
                # Trova gli indici dei dati corrispondenti a questa etichetta
                # Una volta per lo 0 ed una volta per l' 1
                
                label_indices = np.where(subject_labels == label)[0]

                # A quel punto, estrae i dati e le labels per questi indici
                # Una volta per lo 0 ed una volta per l' 1
                
                data_for_label = subject_data[label_indices]
                labels_for_label = subject_labels[label_indices]

                # A quel punto, per ogni soggetto, per ogni condzione sperimentale, 
                # per quelle due labels là (sempre presenti, per ogni coppia di condizioni sperimentali)
                # Una volta per lo 0 ed una volta per l' 1
                
                #Andrà a creare per ogni etichetta, una chiave che si chiamerà 
                #o 0 od 1 (inizialmente, vuoto -> perché deve esser inizializzato)
                #E poi, dopo, ci appenderà le labels 
                 # Una volta per lo 0 ed una volta per l' 1
                #  Di quel soggetto per quella coppia di condizioni sperimentali iterate a quel momento
                
                #Aggiunge ai dizionari globali, creando la chiave se non esiste
                if label not in data_by_label:
                    data_by_label[label] = []
                    labels_by_label[label] = []

                data_by_label[label].append(data_for_label)
                labels_by_label[label].append(labels_for_label)
                
                 # **Salva la shape delle etichette per il soggetto corrente**
                shape_labels_per_subject[label].append(labels_for_label.shape[0])  # Aggiungi solo la dimensione (numero di etichette)

        
                # **Aggiungi un print di controllo per ogni soggetto**
                print(f"Soggetto: \033[1m{subject_key}\033[0m, Condizione: \033[1m{condition_triplet}\033[0m, Etichetta: \033[1m{label}\033[0m, Shape: \033[1m{labels_for_label.shape[0]}\033[0m")
                #print(f"  - Numero di \033[1mdati\033[0m per {label}: {data_for_label.shape[0]}")
                #print(f"  - Numero di \033[1metichette\033[0m per {label}: {labels_for_label.shape[0]}")
                
                    
        # Dopodiché, vado a creare invece i dizionari che conterranno
        # Le concatenazioni, di dati e labels corrispondenti, di tutti i soggetti per cui l'etichetta era 
        # o 0 od 1 
        
        # Di conseguenza, qui dentro dovrei avere, per ogni coppia di condizioni sperimentali
        # Tutti gli 0 ed 1 (ed i relativi dati corrispondenti)
        # di tutti i soggetti, ma concatenati
        
        
        concatenated_data_by_label = {}
        concatenated_labels_by_label = {}

        for label in data_by_label.keys():
            concatenated_data_by_label[label] = np.vstack(data_by_label[label])
            concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
            
            # **Calcolare la shape totale delle etichette**
            #total_labels_0 = np.sum(1 for subject_labels in labels_by_label[label] if 0 in subject_labels)
            #total_labels_1 = np.sum(1 for subject_labels in labels_by_label[label] if 1 in subject_labels)
            #total_labels = total_labels_0 + total_labels_1

            # **Determinare gli indici delle etichette 0 e 1 nell'array finale**
            
            # Gli indici delle etichette 0
            indices_labels_0 = np.where(concatenated_labels_by_label[label] == 0)[0]
            
            # Gli indici delle etichette 1
            indices_labels_1 = np.where(concatenated_labels_by_label[label] == 1)[0]
            
            # Gli indici delle etichette 2
            indices_labels_2 = np.where(concatenated_labels_by_label[label] == 2)[0]
            
            # Indici iniziale e finale per le etichette 0 e 1
            start_idx_0 = indices_labels_0[0] if len(indices_labels_0) > 0 else None
            end_idx_0 = indices_labels_0[-1] if len(indices_labels_0) > 0 else None
            
            start_idx_1 = indices_labels_1[0] if len(indices_labels_1) > 0 else None
            end_idx_1 = indices_labels_1[-1] if len(indices_labels_1) > 0 else None
            
            start_idx_2 = indices_labels_2[0] if len(indices_labels_2) > 0 else None
            end_idx_2 = indices_labels_2[-1] if len(indices_labels_2) > 0 else None
    
    
            # **Print finale per verificare la concatenazione per ogni label**
            #print(f"\nCondizione: \033[1m{condition_triplet}\033[0m, Etichetta: {label}")
            #print(f"  - Shape dei dati concatenati per \033[1m{label}\033[0m: {concatenated_data_by_label[label].shape}")
            #print(f"  - Shape delle etichette concatenate per \033[1m{label}\033[0m: {concatenated_labels_by_label[label].shape}")
            
            # **Stampa la lista delle shapes delle etichette per ogni soggetto per questa etichetta**
            #print(f"\n  - Shape delle etichette per soggetto (per etichetta {label}): {shape_labels_per_subject[label]}\n")

            
            # **Stampa il conteggio totale delle etichette**
            #print(f"\n  - Totale delle etichette 0: {total_labels_0}")
            #print(f"  - Totale delle etichette 1: {total_labels_1}")
            #print(f"  - Totale delle etichette per la condizione: {total_labels}\n")

            # **Stampa gli indici per le etichette 0 e 1**
            # **OSSIA --> Stampa gli indici per l'etichetta corrente**
            
            #if label == 0:
            #    print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #else:
            #    print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}\n")

    
            #print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}")

    
        #ARRIVATI FINO A QUI, abbiamo che siccome stiamo iterando prima per tutti gli 0 e poi per tutti gli 1
        #Significa che, assumendo che siamo dentro 'baseline_vs_th_resp' e che 
        
        #'baseline' sia rappresentato dalle etichette 0
        #'th_resp' sia rappresentato dalle etichette 1
        
        #Al PRIMO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'baseline' per 'baseline_vs_th_resp'di tutti i soggetti)
        
        #Al SECONDO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #Quindi mi manca ancora 
        
        #A) CONCATENARE I DATI:
        
        #1)prima tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        
        #che verrà fatto dentro all_data (che è anch'esso una variabile dinamica!)
        
        #B) CONCATENARE LE LABELS:
        
        #1)prima tutti le labels (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti le labels (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #che verrà fatto dentro all_labels (che è anch'esso una variabile dinamica!)
        
        # Liste per raccogliere dati e labels di tutte le etichette
        
        # Qui dentro, invece, dov con
        all_data = []
        all_labels = []

        for label in concatenated_data_by_label.keys():
            all_data.append(concatenated_data_by_label[label])
            all_labels.append(concatenated_labels_by_label[label])
        
        
        #Alla fine, qui dentro avrò che, PER OGNI COPPIA DI CONDIZIONI SPERIMENTALI
        
        
        #'final_data' dovrebbe avere 
            #- prima tutti i dati di tutti i soggetti associati all'etichetta 0 
            #- e poi tutti i dati di tutti i soggetti associati all'etichetta 1
        
        #'final_labels' dovrebbe avere 
            #- prima tutte le labels di tutti i soggetti associati all'etichetta 0
            #- e poi tutte tutte le labels di tutti soggetti associati all'etichetta 1...

        
        # Concatenazione finale per la condizione corrente
        final_data = np.vstack(all_data)
        final_labels = np.hstack(all_labels)
    
        
        # Nome dinamico del dizionario
        dict_name = f"{prefix}{condition_triplet}{suffix}"

        # Salva il risultato nel dizionario globale
        all_subj_data_by_coupled_cond[dict_name] = {
            'data': final_data,
            'labels': final_labels
        }
        
    # Dopo aver costruito tutti i sotto-dizionari, iterare per stampare gli intervalli
    print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")

    for cond_key, cond_data in all_subj_data_by_coupled_cond.items():
        print(f"Condizione: \033[1m{cond_key}\033[0m\n")

        # Estrai le etichette dal sotto-dizionario
        labels = cond_data['labels']

        # Conta le etichette uniche
        unique_labels = np.unique(labels)

        # Variabile per il conteggio totale delle etichette
        total_labels = 0

        # Stampa gli intervalli di indici per ciascuna etichetta
        for label in unique_labels:

            # Trova gli indici corrispondenti a questa etichetta
            label_indices = np.where(labels == label)[0]

            # Determina l'intervallo
            start_idx = label_indices[0]
            end_idx = label_indices[-1]

            # Aggiungi il numero di occorrenze al conteggio totale
            total_labels += len(label_indices)

            # Stampa l'intervallo
            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m (Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

        # Stampa il totale delle etichette per la condizione corrente
        print(f"\nTotale etichette (0, 1 e 2): \033[1m{total_labels}\033[0m\n")

    return all_subj_data_by_coupled_cond

In [ ]:
# Parametri

#baseline_vs_th_resp_vs_pt_resp
#baseline_vs_th_resp_vs_shared_resp
#baseline_vs_pt_resp_vs_shared_resp
#th_resp_vs_pt_resp_vs_shared_resp

conditions = ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp','baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']

prefix = "new_all_th_concat_reconstructions_"
suffix = "_1_45"

tripled_conditions = list(new_subject_level_concatenations_triplets_exp_th_1_45['th_1'].keys())

# Chiamata alla funzione
new_concatenated_dictionaries_th = concatenate_all_single_subj_tripled_experimental_conditions_th(
    data_structure=new_subject_level_concatenations_triplets_exp_th_1_45,
    conditions=tripled_conditions,
    prefix=prefix,
    suffix=suffix
)

# Stampa i risultati per verifica
print('\n\033[1mRISULTATO FINALE TUTTI I SOGGETTI TH\033[0m') 
for key, value in new_concatenated_dictionaries_th.items():
    print(f"{key}:")
    print(f"  Dati: {value['data'].shape}")
    print(f"  Labels: {value['labels'].shape}")


#### STEP 6.3.2.2 - Salvataggio Dataset di **All Single Therapists** EEG Preprocessed Data (1-45Hz) across **Triplets of Experimental Conditions** INSIEME

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE_1_45

In [ ]:
new_concatenated_dictionaries_th.keys()

In [ ]:
#Mi estraggo ogni sotto-dizionario

new_all_th_concat_reconstructions_baseline_vs_th_resp_vs_pt_resp_1_45 = new_concatenated_dictionaries_th['new_all_th_concat_reconstructions_baseline_vs_th_resp_vs_pt_resp_1_45']

new_all_th_concat_reconstructions_baseline_vs_th_resp_vs_shared_resp_1_45 = new_concatenated_dictionaries_th['new_all_th_concat_reconstructions_baseline_vs_th_resp_vs_shared_resp_1_45']

new_all_th_concat_reconstructions_baseline_vs_pt_resp_vs_shared_resp_1_45 = new_concatenated_dictionaries_th['new_all_th_concat_reconstructions_baseline_vs_pt_resp_vs_shared_resp_1_45']

new_all_th_concat_reconstructions_th_resp_vs_pt_resp_vs_shared_resp_1_45 = new_concatenated_dictionaries_th['new_all_th_concat_reconstructions_th_resp_vs_pt_resp_vs_shared_resp_1_45']


In [ ]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_NF '''
import pickle
   
base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#'BASELINE VS TH RESP VS PT RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_baseline_vs_th_resp_vs_pt_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_baseline_vs_th_resp_vs_pt_resp_1_45, f)
                                  
#'BASELINE VS TH RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_baseline_vs_th_resp_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_baseline_vs_th_resp_vs_shared_resp_1_45, f)
        
#'BASELINE VS PT RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_baseline_vs_pt_resp_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_baseline_vs_pt_resp_vs_shared_resp_1_45, f)
    
#'TH RESP VS PT RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_th_concat_reconstructions_th_resp_vs_pt_resp_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_th_concat_reconstructions_th_resp_vs_pt_resp_vs_shared_resp_1_45, f)


### STEP 6.1.3: Mi salvo le strutture dati dei singoli PAZIENTI in dizionari annidati (EEG 1-45Hz)

#### Descrizione per codice:

Aiutami a convertire questa struttura dati in un dizionario annidato

**patients_data_to_dict** è una copia di '**patients_data**' fatto così

è una **lista di dizionari**
dove per **ogni indice** della lista, ci sono **i dati del singolo soggetto contenuti dentro un dizionario**, che avrà 8 elementi che son **8 chiavi-valore**, 

<br>

**Struttura Originaria**

**patient_data** = 

[{'**pt_1**': {'baseline_1': np.array, 'vision_resp_1': np.array, 'th_resp_1': np.array, 'shared_resp_1'np.array,
           'baseline_1_labels': list, 'vision_resp_1_labels': list, 'th_resp_1_labels': list, 
           'shared_resp_1_labels': list},
           
{'**pt_2**': {'baseline_2': np.array, 'vision_resp_2': np.array, 'th_resp_2': np.array, 'shared_resp_2': np.array,
           'baseline_2_labels': list, 'vision_resp_2_labels': list, 'th_resp_2_labels': list 
           'shared_resp_2_labels': list},
           etc... ]
           
           
<br>

quelle **senza '_labels' contengono i dati np.array**, quelle **con '_labels'** contengono **le rispettive etichette, dentro una lista, che vanno convertite in un array numpy** ...

ossia per il primo soggetto, ad esempio, abbiamo che la struttura dati è cpsì

patients_data[0].keys()
dict_keys(['baseline_1', 'vision_resp_1', 'th_resp_1', 'shared_resp_1', 'baseline_1_labels', 'vision_resp_1_labels', 'th_resp_1_labels', 'shared_resp_1_labels'])

le chiavi con '_labels' son quelle con le labels corrispondenti della chiave che ha la stringa senza '_labels'..

Ora, vorrei per ogni indice della lista (quindi per **ogni dizionario associato ad un paziente**), vorrei che:

**1)** mi convertissi i valori delle chiavi con labels in delle numpy array 

**2)** mi concatenassi i rispettivi dati e labels con la stessa corrispondenza tra dati e label 

in sintesi vorrei che ci fosse un dizionario annidato che avesse questa struttura

**pt_data_dict** = 

{'**pt_1**': {'data': np.array (i.e., tutti i trials concantenati del soggetto pt_1) 
                                            'labels':np.array (i.e., tutte labels dei trials concantenati del soggetto pt_1)}

{'**pt_2**': {'data': np.array (i.e., tutti i trials concantenati del soggetto pt_2) 
                                            'labels':np.array (i.e., tutte labels dei trials concantenati del soggetto pt_2)}
<br>


#### Implementazione del codice:

In [ ]:
!pwd

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/patients_data.pkl', 'rb') as f:
    patients_data = pickle.load(f)

In [ ]:
patients_data_to_dict = cp.deepcopy(patients_data)
#len(therapists_data_to_dict[0])
patients_data_to_dict[0].keys()

In [ ]:
import numpy as np

# Dizionario finale annidato per tutti i terapisti
pt_data_dict = {}

# Iteriamo su ogni soggetto
for idx, patient_data_dict in enumerate(patients_data_to_dict):
    # Creiamo le liste per accumulare dati e labels
    data_list = []
    labels_list = []

    # Iteriamo su ogni chiave-valore del dizionario del singolo terapista
    for key, value in patient_data_dict.items():
        if '_labels' in key:
            # Convertiamo le labels in np.array e le aggiungiamo alla lista delle labels
            labels_list.append(np.array(value))
        else:
            # Aggiungiamo i dati alla lista dei dati
            data_list.append(value)

    # Concatenazione di tutti i dati e labels per il terapista corrente
    concatenated_data = np.concatenate(data_list, axis=0)
    concatenated_labels = np.concatenate(labels_list, axis=0)

    # Creiamo una chiave unica per il terapista (ad esempio th_1, th_2, ecc.)
    patient_key = f'pt_{idx + 1}'

    # Aggiungiamo al dizionario finale
    pt_data_dict[patient_key] = {
        'data': concatenated_data,
        'labels': concatenated_labels
    }

# Ora th_data_dict conterrà i dati e le labels concatenati per ciascun soggetto
#print(pt_data_dict)


In [ ]:
# Iteriamo sul dizionario annidato th_data_dict
for patient, data_labels in pt_data_dict.items():
    print(f"Patient: \033[1m{patient}\033[0m")
    
    # Iteriamo su ogni sottochiave (data e labels) del dizionario annidato
    for key, value in data_labels.items():
        print(f"  {key}: {value.shape}")  # Stampiamo la chiave e la shape del valore


In [ ]:
!pwd

In [ ]:
'''PER SALVARE STRUTTURA DATI E LABEL OGNI SOGGETTO NON ANCORA CONCATENATI TRA DI LORO

PS: viene comunque già salvato in  --> new_subject_level_concatenations_pt_1_20 '''

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('pt_data_dict.pkl', 'wb') as f:
#    pickle.dump(pt_data_dict, f) 

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
#pwd
#cd ..
#cd New_Plots_Sliding_Estimator_MNE

#path corretta --> cd Plots_Sliding_Estimator_MNE
#path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"

#Comandi da eseguire

#!pwd
#cd Plots_Sliding_Estimator_MNE


import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'
#f'{base_path}/

# Salva il dizionario th_data_dict in un file pkl
with open(f'{base_path}/new_subject_level_concatenations_pt_1_45.pkl', 'wb') as file:
    pickle.dump(pt_data_dict, file)

#print("Dati concantenati dei Singoli Terapisti salvati in 'subject_level_concatenations_th_1_20.pkl'")


### STEP 6.1.3.1: Mi concateno le strutture dati e labels dei singoli PAZIENTI (EEG 1-45Hz) INSIEME

In [ ]:
!pwd

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'
#f'{base_path}/

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_subject_level_concatenations_pt_1_45.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_45 = pickle.load(f)

In [ ]:
print(new_subject_level_concatenations_pt_1_45.keys())
print()
print(new_subject_level_concatenations_pt_1_45['pt_1'].keys())

In [ ]:
''' 
                                            OLD APPROACH SBAGLIATO!
import numpy as np

# Crea liste vuote per raccogliere i dati e le labels di tutti i soggetti
all_data = []
all_labels = []

# Itera sui soggetti e aggiungi i dati e le labels alle liste
for subject_key in new_subject_level_concatenations_pt_1_45.keys():
    subject_data = new_subject_level_concatenations_pt_1_45[subject_key]['data']
    subject_labels = new_subject_level_concatenations_pt_1_45[subject_key]['labels']
    
    all_data.append(subject_data)
    all_labels.append(subject_labels)

# Concatena tutti i dati e le labels lungo l'asse 0
concatenated_data = np.vstack(all_data)
concatenated_labels = np.hstack(all_labels)

# Ora concatenated_data e concatenated_labels contengono i dati e le labels di tutti i soggetti concatenati
print("Forma dei dati concatenati:", concatenated_data.shape)
print("Lunghezza delle labels concatenate:", concatenated_labels.shape)

'''

In [ ]:
# Dizionario per raccogliere dati e labels ordinati per etichetta
data_by_label = {}
labels_by_label = {}

# Itera sui soggetti
for subject_key in new_subject_level_concatenations_pt_1_45.keys():
    subject_data = new_subject_level_concatenations_pt_1_45[subject_key]['data']
    subject_labels = new_subject_level_concatenations_pt_1_45[subject_key]['labels']
    
    # Trova le etichette uniche e gli indici corrispondenti
    unique_labels = np.unique(subject_labels)
    
    for label in unique_labels:
        # Trova gli indici dei dati corrispondenti a questa etichetta
        label_indices = np.where(subject_labels == label)[0]
        
        # Estrai i dati e le labels per questi indici
        data_for_label = subject_data[label_indices]
        labels_for_label = subject_labels[label_indices]
        
        # Aggiungi ai dizionari globali, creando la chiave se non esiste
        if label not in data_by_label:
            data_by_label[label] = []
            labels_by_label[label] = []
        
        data_by_label[label].append(data_for_label)
        labels_by_label[label].append(labels_for_label)

# Concatena i dati e le labels per ogni etichetta
concatenated_data_by_label = {}
concatenated_labels_by_label = {}

for label in data_by_label.keys():
    concatenated_data_by_label[label] = np.vstack(data_by_label[label])
    concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
    
    concatenated_data = concatenated_data_by_label[label]
    concatenated_data = concatenated_labels_by_label
    
# Risultato finale: concatenati per etichetta
print("Dati concatenati per etichetta:")
for label in concatenated_data_by_label.keys():
    print(f"Etichetta {label}: {concatenated_data_by_label[label].shape}, {concatenated_labels_by_label[label].shape}")


In [ ]:
# Liste per raccogliere dati e labels di tutte le etichette
all_data = []
all_labels = []

# Itera su tutte le etichette
for label in concatenated_data_by_label.keys():
    all_data.append(concatenated_data_by_label[label])  # Aggiungi i dati concatenati per l'etichetta
    all_labels.append(concatenated_labels_by_label[label])  # Aggiungi le labels concatenate per l'etichetta

# Concatenazione finale
final_data = np.vstack(all_data)  # Concatena tutti i dati
final_labels = np.hstack(all_labels)  # Concatena tutte le labels

# Crea il dizionario finale
new_all_pt_concat_reconstructions_1_45 = {
    'data': final_data,
    'labels': final_labels
}

# Controllo delle forme
print(f"Forma finale dei dati: {new_all_pt_concat_reconstructions_1_45['data'].shape}")
print(f"Forma finale delle labels: {new_all_pt_concat_reconstructions_1_45['labels'].shape}")

In [ ]:
'''VERIFICA CORRETTA LABELS'''

unique_labels, label_counts = np.unique(final_labels, return_counts=True)

# Stampa le etichette uniche e il loro conteggio
print("Etichette uniche e conteggio:", dict(zip(unique_labels, label_counts)))

# Controlla che la somma delle occorrenze corrisponda al numero totale di righe dei dati
print("Totale righe nei dati:", final_data.shape[0])
print("Somma dei conteggi delle etichette:", np.sum(label_counts))

assert final_data.shape[0] == np.sum(label_counts), "Mismatch tra dati e etichette!"


In [ ]:
for label in unique_labels:
    
    # Trova gli indici delle etichette corrispondenti
    label_indices = np.where(final_labels == label)[0]
    
    # Estrai i dati corrispondenti
    data_for_label = final_data[label_indices, :]
    
    # Controlla che la lunghezza corrisponda al conteggio dell'etichetta
    assert data_for_label.shape[0] == label_counts[np.where(unique_labels == label)[0][0]], \
        f"Mismatch per l'etichetta {label}!"
    
    print(f"Etichetta {label} verificata: {data_for_label.shape[0]} dati trovati.")


In [ ]:
# Estrarre le labels dal dizionario
final_labels = new_all_pt_concat_reconstructions_1_45['labels']

# Etichette uniche presenti
unique_labels = np.unique(final_labels)

print("Intervalli di indici per ciascuna etichetta:")
# Itera su ciascuna etichetta unica
for label in unique_labels:
    # Trova gli indici corrispondenti a questa etichetta
    label_indices = np.where(final_labels == label)[0]
    
    # Determina l'intervallo
    start_idx = label_indices[0]
    end_idx = label_indices[-1]
    
    # Stampa l'intervallo
    print(f"Etichetta {label}: Indici {start_idx}-{end_idx} (totale: {len(label_indices)})")


In [ ]:
'''SALVO I DATI E LABELS CONCATENATI DI TUTTI I SOGGETTI PAZIENTI PER DATI EEG PREPROCESSED 1-45 Hz'''

import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_1_45, f)

### STEP 6.3.1.2 - All Patients EEG Preprocessed Data (1-45Hz) across **Couples of Experimental Conditions**

In [ ]:
!pwd

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'
#f'{base_path}/

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/patients_data.pkl', 'rb') as f:
    patients_data = pickle.load(f)

In [ ]:
patients_data[0].keys()

In [ ]:
print(f"Baseline in PT_1:, {len(patients_data[0]['baseline_1_labels'])}\n")
print(f"Th_Resp in PT_1:, {len(patients_data[0]['th_resp_1_labels'])}\n")
print(f"Pt_Resp in PT_1:, {len(patients_data[0]['pt_resp_1_labels'])}\n")
print(f"Shared_Resp in PT_1:, {len(patients_data[0]['shared_resp_1_labels'])}\n")

In [ ]:
'''
DETAILED VERSION WITH PRINTS

Dettagli della struttura finale
Chiavi di primo livello:
Sono i soggetti, ad esempio 'th_1', 'th_2', ..., 'th_16'.

Chiavi di secondo livello:
Sono le combinazioni delle condizioni sperimentali (es. 'baseline_vs_th_resp').

Chiavi di terzo livello:
Ogni combinazione contiene due chiavi: 

'data' (un array concatenato dei dati delle due condizioni) e 
'labels' (un array concatenato delle etichette 0 e 1).

'''

import itertools
import numpy as np


# Condizioni sperimentali
experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']

# Variabile di output
new_subject_level_concatenations_coupled_exp_pt_1_45 = {}



# Nuova variabile per tracciare il soggetto corrente stampato
last_subject_key = None

# Dizionario per tenere traccia delle combinazioni già stampate per ogni soggetto
#printed_combinations = {}



# Itera su ogni soggetto nella lista therapists_data
for subject_index, subject_data in enumerate(patients_data):
    subject_key = f'pt_{subject_index + 1}'  # Crea la chiave per il soggetto (es. 'th_1', 'th_2', ...)
    
    
    
    '''PER TRACCIARE SOGGETTO PRECEDENTE'''
    # Aggiungi separazione visiva quando cambia il soggetto
    if subject_key != last_subject_key:
        if last_subject_key is not None:  # Evita di stampare separatori prima del primo soggetto
            print("\n" + "-" * 50 + f" END OF {last_subject_key.upper()} " + "-" * 50 + "\n")
        print(f"\nProcessing Subject: {subject_key}\n" + "=" * 80)
        
        # Inizializza il dizionario delle combinazioni stampate per il nuovo soggetto
        #printed_combinations[subject_key] = set()  # Usando un set per evitare duplicati
    
    last_subject_key = subject_key  # Aggiorna il soggetto corrente
    
    
    # Inizializza il dizionario per questo soggetto
    new_subject_level_concatenations_coupled_exp_pt_1_45[subject_key] = {}
    
    '''Creo un suffisso dinamico per 
    1) Estrazione dei dati di una condizione sperimentale di un certo soggetto 
    (i.e., baseline_1 dove "_1" è il suffisso)
    
    2) Estrazione delle labels di una condizione sperimentale di un certo soggetto 
    (i.e., baseline_1_labels dove "_1_labels" è il suffisso)
    '''
    
    # Suffisso dinamico basato sull'indice del soggetto
    data_suffix = f"_{subject_index + 1}"
    labels_suffix = f"{data_suffix}_labels"
    
    # Crea tutte le combinazioni uniche di condizioni sperimentali
    condition_pairs = list(itertools.combinations(experimental_conditions, 2))
    
    # Loop su tutte le combinazioni di condizioni
    for cond_1, cond_2 in condition_pairs:
        condition_pair_key = f"{cond_1}_vs_{cond_2}"  # Nome della combinazione (es. 'baseline_vs_th_resp')
        
        
        # Controlla se la combinazione è già stata stampata per il soggetto corrente
        #if condition_pair_key in printed_combinations[subject_key]:
        #    continue  # Salta la combinazione se è già stata stampata
        
        # Stampa il messaggio per la prima volta che incontriamo questa combinazione
        print(f"\n\t\tCreation of Coupled Condition \033[1m{condition_pair_key}\033[0m")
        
        # Aggiungi la combinazione al set delle combinazioni stampate per il soggetto
        #printed_combinations[subject_key].add(condition_pair_key)
        
        #print(condition_pair_key
                    
        #Estrai i dati e le etichette per le due condizioni
        data_cond_1 = subject_data.get(f"{cond_1}{data_suffix}")
        print(f"Extracting data_cond_1 which is {cond_1}{data_suffix}")
        labels_cond_1 = subject_data.get(f"{cond_1}{labels_suffix}")
        print(f"Extracting labels_cond_1 which is {cond_1}{labels_suffix}")
        
        data_cond_2 = subject_data.get(f"{cond_2}{data_suffix}")
        labels_cond_2 = subject_data.get(f"{cond_2}{labels_suffix}")
        
        # Verifica che i dati e le etichette siano validi
        if data_cond_1 is None or labels_cond_1 is None or data_cond_2 is None or labels_cond_2 is None:
            continue  # Salta se manca qualcosa
        
        # Converti le etichette da lista a numpy array
        labels_cond_1 = np.zeros(len(labels_cond_1), dtype=int)  # Etichette di cond_1 come 0
        labels_cond_2 = np.ones(len(labels_cond_2), dtype=int)   # Etichette di cond_2 come 1
        
        # Concatenazione dei dati e delle etichette
        concatenated_data = np.vstack((data_cond_1, data_cond_2))
        concatenated_labels = np.hstack((labels_cond_1, labels_cond_2))
        
        # Salva i dati concatenati nella struttura
        new_subject_level_concatenations_coupled_exp_pt_1_45[subject_key][condition_pair_key] = {
            'data': concatenated_data,
            'labels': concatenated_labels
        }
        
        # Dopo aver trattato tutti i livelli, aggiungi una separazione visiva per il soggetto
        print("-" * 50 + f"-" * 50)


In [ ]:
#new_subject_level_concatenations_coupled_exp_pt_1_20.keys()
#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1'].keys()
#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp'].keys()
print(f"Data Shape: {new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['baseline_vs_th_resp']['data'].shape}")
print()
print(f"Data Shape: {new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['baseline_vs_th_resp']['labels'].shape}")
print()
print(f"Counts Shape: {np.unique(new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['baseline_vs_th_resp']['labels'], return_counts = True)}")

In [ ]:
print(f"\t\t\t\t\033[1mStructure of new_subject_level_concatenations_coupled_exp_pt_1_45\033[0m: \n")
print(f"\033[1mFirst Order Keys\033[0m: {new_subject_level_concatenations_coupled_exp_pt_1_45.keys()}\n")
print(f"\033[1mSecond Order Keys\033[0m: {new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1'].keys()}\n")
print(f"\033[1mThird Order Keys\033[0m: \n{new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['baseline_vs_th_resp'].keys()}\n")

In [ ]:
'''VERIFICO CHE LA CONCATENAZIONE SIA AVVENUTA CORRETTAMENTE!'''

print("\tNOW, LET US SEE IF THE CONCATENATIONS RESPECT THE ORIGINAL SHAPES FOR EVERY COUPLED EXPERIMENTAL CONDITION!")
print("\tFOR THE 1°ST SUBJECT: CHECK IF THE SUM OF INDIVIDUAL EXP COND SHAPE MATCHES THE COUPLED COND CONCATENATION SHAPE:\n\n")

print("\033[1mINDIVIDUAL EXP COND SHAPE OF FIRST SUBJECT\033[0m:")


print(f"Baseline in PT_1: {len(patients_data[0]['baseline_1_labels'])}\n")
print(f"Th_Resp in PT_1: {len(patients_data[0]['th_resp_1_labels'])}\n")
print(f"Pt_Resp in PT_1: {len(patients_data[0]['pt_resp_1_labels'])}\n")
print(f"Shared_Resp in PT_1: {len(patients_data[0]['shared_resp_1_labels'])}\n")
print()

#new_subject_level_concatenations_coupled_exp_pt_1_20['th_1']['baseline_vs_th_resp']['data'].shape
#new_subject_level_concatenations_coupled_exp_pt_1_20['th_1']['baseline_vs_th_resp']['labels'].shape

# Seleziona il primo soggetto (ad esempio, 'th_1')
subject_key = 'pt_1'


# Itera per il soggetto
for condition_pair_key, pair_data in new_subject_level_concatenations_coupled_exp_pt_1_45[subject_key].items():
 
    # Estrai i dati e le etichette per ogni coppia di condizioni
    data = pair_data.get('data')
    labels = pair_data.get('labels')

    # Stampa il nome della coppia di condizioni e le loro dimensioni
    print(f"Condition Pair: \033[1m{condition_pair_key}\033[0m")

    if data is not None and labels is not None:
        print(f"  Data Shape: {data.shape}")
        print(f"  Labels Shape: {labels.shape}")
    else:
        print("  Missing data or labels!")

In [ ]:
print(np.unique(new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['baseline_vs_th_resp']['labels'], return_counts = True))
print(np.unique(new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['th_resp_vs_shared_resp']['labels'], return_counts = True))

In [ ]:
print(f"\t\t\t\033[1mBASELINE_VS_TH_RESP\033[0m")
print(new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['baseline_vs_th_resp']['labels'][:44])
print()
print(new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['baseline_vs_th_resp']['labels'][44:])
print()
print(f"\t\t\t\033[1mTH_RESP_VS_SHARED_RESP\033[0m")
print(new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['th_resp_vs_shared_resp']['labels'][:40])
print()
print(new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['th_resp_vs_shared_resp']['labels'][40:])

#### STEP 6.3.1.3 - Salvataggio Dataset di All Single Patients EEG Preprocessed Data (1-20Hz) across Couples of Experimental Conditions

In [ ]:
!pwd

In [ ]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_1_45'''
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'


# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_subject_level_concatenations_coupled_exp_pt_1_45.pkl', 'wb') as f:
    pickle.dump(new_subject_level_concatenations_coupled_exp_pt_1_45, f)

### STEP 6.3.2 Mi concanteno All Single Patients EEG Preprocessed Data (1-45Hz) across **Couples of Experimental Conditions**

#### Istruzioni

Perfetto, ora vorrei che, nel prossimo codice che vorrei mi aiutassi a creare, dovresti fare la stessa cosa, ma per una struttura con un livello in più che avrebbe ad esempio questa struttura..


print(new_subject_level_concatenations_coupled_exp_th_1_45.keys())
print()
print(new_subject_level_concatenations_coupled_exp_th_1_45['th_1'].keys())
print(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp'].keys())
print(np.unique(new_subject_level_concatenations_coupled_exp_th_1_45['th_1']['baseline_vs_th_resp']['labels'], return_counts = True))

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16', 'th_17', 'th_18', 'th_19', 'th_20'])

dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])
dict_keys(['data', 'labels'])
(array([0, 1]), array([44, 40]))

ogni condizione sperimentale ('baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp') avrebbe i dati e labels in sostanza associati alla coppia di condizioni sperimentali, dove, la prima stringa della chiave della condizione sperimentale corrisponde alle etichette 0, e l'altra 1.

ora, io vorrei che, per ogni soggetto, 

1) tu identifichi la specifica chiave associata alla stessa condizione sperimetnale,

2) entri dentro quella chiave e prendi i dati e le labels di ogni soggetto e li concateni uno sotto l'altro, come prima.

3) vorrei avere, alla fine, che si creassero una serie di nuovi dizionari, che si chiameranno similarmente. 

nello specifico avranno un prefisso, un termine dinamico ed un suffisso...

- il prefisso sarà "new_all_th_concat_reconstructions_" 

-il termine dinamico cambierà, a seconda della condizione sperimentale iterata in quel momento, che sarebbe tra quelle condizioni sperimentali iterate ('baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp') 

-il suffisso, che sarebbe "_1_45"..

in sostanza dovrebbe apparire una cosa del genere :

"new_all_th_concat_reconstructions_{condition_pair}_1_45"

alla fine, dovrei avere, se non sbaglio, 6 dizionari, ciascuno che conterrà il set di dati e labels di tutti i terapisti per tutte le combinazioni possibili di coppie di condizioni sperimentali.

ti è chiaro cosa vorrei che facessi ora?

<br>


**CHAT**

Sì, mi è chiaro cosa vuoi fare. Ecco un riassunto dei passaggi:

Iterare su ciascuna condizione sperimentale: Ogni chiave della struttura new_subject_level_concatenations_coupled_exp_th_1_45['th_1'] rappresenta una condizione sperimentale (es. 'baseline_vs_th_resp', ecc.).

Concatenare i dati e le etichette: Per ogni condizione sperimentale, estrarre i dati ('data') e le etichette ('labels') di tutti i soggetti e concatenarli.

Creare dizionari per ogni condizione sperimentale: Creare un dizionario con il nome dinamico basato sulla condizione sperimentale, come "new_all_th_concat_reconstructions_{condition_pair}_1_45", contenente i dati concatenati e le etichette concatenate.



**IO**

Per fare questo in maniera più elegante, crea una funzione, che ritorna in un dizionario tutti e 6 i sotto-dizionari nuovi, ciascuno che conterrà il set di dati e labels di tutti i terapisti per tutte le combinazioni possibili di coppie di condizioni sperimentali! 


#### Implementazione 

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_subject_level_concatenations_coupled_exp_pt_1_45.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt_1_45 = pickle.load(f)

In [ ]:
print(new_subject_level_concatenations_coupled_exp_pt_1_45.keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1'].keys())
print(new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['baseline_vs_th_resp'].keys())
print(np.unique(new_subject_level_concatenations_coupled_exp_pt_1_45['pt_1']['baseline_vs_th_resp']['labels'], return_counts = True))

In [ ]:
def concatenate_all_single_subj_coupled_experimental_conditions_pt(data_structure, conditions, prefix, suffix):
    
    """
    Concatena i dati e le etichette per ogni condizione sperimentale da una struttura dati con un livello in più,
    ordinandoli anche per etichetta.

    Parameters:
        data_structure (dict): La struttura dati di input che contiene i dati per soggetti e condizioni.
        conditions (list): Le condizioni sperimentali (chiavi del secondo livello) da processare.
        prefix (str): Il prefisso del nome dinamico del dizionario.
        suffix (str): Il suffisso del nome dinamico del dizionario.

    Returns:
        dict: Un dizionario contenente i nuovi dizionari con i dati concatenati e le etichette per ogni condizione.
    """
    
    #Questo conterrà i dati complessivi di tutti i soggetti per ogni coppia di condizioni sperimentali
    all_subj_data_by_coupled_cond = {}

    # Itera su ogni condizione sperimentale
    for condition_pair in conditions:
        
        # Dizionari per raccogliere dati e labels ordinati per ogni coppia di condizioni sperimentali
        # che è dinamico, per ogni coppia di condizioni sperimentali 
        
        #(quindi si ricreeranno passando alla condizione sperimentale successiva!)
        
        data_by_label = {}
        labels_by_label = {}
        
        
        # Lista temporanea per salvare la shape delle etichette per ogni soggetto per ogni etichetta iterata
        
        '''
        Per ogni condizione sperimentale, per ognuna delle 2 labels, 
        la shape delle etichette per ogni soggetto, 

        e me le salvi dentro una lista temporanea, che salva in formato la shape (solo il valore numerico) di ogni soggetto 
        per l'etichette iterata per quella condizione sperimentale là.

        poi, a questo livello dei print 

         # **Print finale per verificare la concatenazione per ogni label**
            print(f"Condizione: {condition_pair}, Etichetta: {label}")
            print(f"  - Shape dei dati concatenati per {label}: {concatenated_data_by_label[label].shape}")
            print(f"  - Shape delle etichette concatenate per {label}: {concatenated_labels_by_label[label].shape}")

        vorrei che mi stampassi anche questa lista alla fine del print, di modo che possa vedere visivamente subito il numero di labels di ogni soggetto associate a quella labels iterata là così da vedere se il conteggio corrisponde visivamente al totale salvate dentro 

        "concatenated_data_by_label[label]"
        '''
        
        shape_labels_per_subject = {0: [], 1: []}  # Inizializza un dizionario per le etichette 0 e 1


        # Itera su tutti i soggetti
        # In questo caso, itera sulle chiavi di ogni soggetto
        
        # Quindi prenderà, per la relativa coppia di condizioni sperimentali di ogni soggetto,
        # i dati e le labels di quel soggetto, per quella relativa coppia di condizioni sperimentali
        
        for subject_key in data_structure.keys():
            
            
            # Qui estrae i dati e le labels per questa condizione sperimentale di quel soggettio lì
            subject_data = data_structure[subject_key][condition_pair]['data']
            subject_labels = data_structure[subject_key][condition_pair]['labels']

            # Trova le etichette uniche e gli indici corrispondenti per quella coppia di condizioni sperimentali lì,
            # Ossia, potrà trovare gli 0 e gli 1 
            
            unique_labels = np.unique(subject_labels)
        
            #A quel punto, per ognuna delle due labels trovate per quella coppia di condizioni sperimentali lì
            #Che saranno sempre o 0 o 1
            
            for label in unique_labels:
                
                # Trova gli indici dei dati corrispondenti a questa etichetta
                # Una volta per lo 0 ed una volta per l' 1
                
                label_indices = np.where(subject_labels == label)[0]

                # A quel punto, estrae i dati e le labels per questi indici
                # Una volta per lo 0 ed una volta per l' 1
                
                data_for_label = subject_data[label_indices]
                labels_for_label = subject_labels[label_indices]

                # A quel punto, per ogni soggetto, per ogni condzione sperimentale, 
                # per quelle due labels là (sempre presenti, per ogni coppia di condizioni sperimentali)
                # Una volta per lo 0 ed una volta per l' 1
                
                #Andrà a creare per ogni etichetta, una chiave che si chiamerà 
                #o 0 od 1 (inizialmente, vuoto -> perché deve esser inizializzato)
                #E poi, dopo, ci appenderà le labels 
                 # Una volta per lo 0 ed una volta per l' 1
                #  Di quel soggetto per quella coppia di condizioni sperimentali iterate a quel momento
                
                #Aggiunge ai dizionari globali, creando la chiave se non esiste
                if label not in data_by_label:
                    data_by_label[label] = []
                    labels_by_label[label] = []

                data_by_label[label].append(data_for_label)
                labels_by_label[label].append(labels_for_label)
                
                 # **Salva la shape delle etichette per il soggetto corrente**
                shape_labels_per_subject[label].append(labels_for_label.shape[0])  # Aggiungi solo la dimensione (numero di etichette)

        
                # **Aggiungi un print di controllo per ogni soggetto**
                print(f"Soggetto: \033[1m{subject_key}\033[0m, Condizione: \033[1m{condition_pair}\033[0m, Etichetta: \033[1m{label}\033[0m, Shape: \033[1m{labels_for_label.shape[0]}\033[0m")
                #print(f"  - Numero di \033[1mdati\033[0m per {label}: {data_for_label.shape[0]}")
                #print(f"  - Numero di \033[1metichette\033[0m per {label}: {labels_for_label.shape[0]}")
                
                    
        # Dopodiché, vado a creare invece i dizionari che conterranno
        # Le concatenazioni, di dati e labels corrispondenti, di tutti i soggetti per cui l'etichetta era 
        # o 0 od 1 
        
        # Di conseguenza, qui dentro dovrei avere, per ogni coppia di condizioni sperimentali
        # Tutti gli 0 ed 1 (ed i relativi dati corrispondenti)
        # di tutti i soggetti, ma concatenati
        
        
        concatenated_data_by_label = {}
        concatenated_labels_by_label = {}

        for label in data_by_label.keys():
            concatenated_data_by_label[label] = np.vstack(data_by_label[label])
            concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
            
            # **Calcolare la shape totale delle etichette**
            #total_labels_0 = np.sum(1 for subject_labels in labels_by_label[label] if 0 in subject_labels)
            #total_labels_1 = np.sum(1 for subject_labels in labels_by_label[label] if 1 in subject_labels)
            #total_labels = total_labels_0 + total_labels_1

            # **Determinare gli indici delle etichette 0 e 1 nell'array finale**
            
            # Gli indici delle etichette 0
            indices_labels_0 = np.where(concatenated_labels_by_label[label] == 0)[0]
            
            # Gli indici delle etichette 1
            indices_labels_1 = np.where(concatenated_labels_by_label[label] == 1)[0]
            
            # Indici iniziale e finale per le etichette 0 e 1
            start_idx_0 = indices_labels_0[0] if len(indices_labels_0) > 0 else None
            end_idx_0 = indices_labels_0[-1] if len(indices_labels_0) > 0 else None
            start_idx_1 = indices_labels_1[0] if len(indices_labels_1) > 0 else None
            end_idx_1 = indices_labels_1[-1] if len(indices_labels_1) > 0 else None
    
    
            # **Print finale per verificare la concatenazione per ogni label**
            #print(f"\nCondizione: \033[1m{condition_pair}\033[0m, Etichetta: {label}")
            #print(f"  - Shape dei dati concatenati per \033[1m{label}\033[0m: {concatenated_data_by_label[label].shape}")
            #print(f"  - Shape delle etichette concatenate per \033[1m{label}\033[0m: {concatenated_labels_by_label[label].shape}")
            
            # **Stampa la lista delle shapes delle etichette per ogni soggetto per questa etichetta**
            #print(f"\n  - Shape delle etichette per soggetto (per etichetta {label}): {shape_labels_per_subject[label]}\n")

            
            # **Stampa il conteggio totale delle etichette**
            #print(f"\n  - Totale delle etichette 0: {total_labels_0}")
            #print(f"  - Totale delle etichette 1: {total_labels_1}")
            #print(f"  - Totale delle etichette per la condizione: {total_labels}\n")

            # **Stampa gli indici per le etichette 0 e 1**
            # **OSSIA --> Stampa gli indici per l'etichetta corrente**
            
            #if label == 0:
            #    print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #else:
            #    print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}\n")

    
            #print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}")

    
        #ARRIVATI FINO A QUI, abbiamo che siccome stiamo iterando prima per tutti gli 0 e poi per tutti gli 1
        #Significa che, assumendo che siamo dentro 'baseline_vs_th_resp' e che 
        
        #'baseline' sia rappresentato dalle etichette 0
        #'th_resp' sia rappresentato dalle etichette 1
        
        #Al PRIMO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'baseline' per 'baseline_vs_th_resp'di tutti i soggetti)
        
        #Al SECONDO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #Quindi mi manca ancora 
        
        #A) CONCATENARE I DATI:
        
        #1)prima tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        
        #che verrà fatto dentro all_data (che è anch'esso una variabile dinamica!)
        
        #B) CONCATENARE LE LABELS:
        
        #1)prima tutti le labels (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti le labels (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #che verrà fatto dentro all_labels (che è anch'esso una variabile dinamica!)
        
        # Liste per raccogliere dati e labels di tutte le etichette
        
        # Qui dentro, invece, dov con
        all_data = []
        all_labels = []

        for label in concatenated_data_by_label.keys():
            all_data.append(concatenated_data_by_label[label])
            all_labels.append(concatenated_labels_by_label[label])
        
        
        #Alla fine, qui dentro avrò che, PER OGNI COPPIA DI CONDIZIONI SPERIMENTALI
        
        
        #'final_data' dovrebbe avere 
            #- prima tutti i dati di tutti i soggetti associati all'etichetta 0 
            #- e poi tutti i dati di tutti i soggetti associati all'etichetta 1
        
        #'final_labels' dovrebbe avere 
            #- prima tutte le labels di tutti i soggetti associati all'etichetta 0
            #- e poi tutte tutte le labels di tutti soggetti associati all'etichetta 1...

        
        # Concatenazione finale per la condizione corrente
        final_data = np.vstack(all_data)
        final_labels = np.hstack(all_labels)
    
        
        # Nome dinamico del dizionario
        dict_name = f"{prefix}{condition_pair}{suffix}"

        # Salva il risultato nel dizionario globale
        all_subj_data_by_coupled_cond[dict_name] = {
            'data': final_data,
            'labels': final_labels
        }
        
    # Dopo aver costruito tutti i sotto-dizionari, iterare per stampare gli intervalli
    print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")

    for cond_key, cond_data in all_subj_data_by_coupled_cond.items():
        print(f"Condizione: \033[1m{cond_key}\033[0m\n")

        # Estrai le etichette dal sotto-dizionario
        labels = cond_data['labels']

        # Conta le etichette uniche
        unique_labels = np.unique(labels)

        # Variabile per il conteggio totale delle etichette
        total_labels = 0

        # Stampa gli intervalli di indici per ciascuna etichetta
        for label in unique_labels:

            # Trova gli indici corrispondenti a questa etichetta
            label_indices = np.where(labels == label)[0]

            # Determina l'intervallo
            start_idx = label_indices[0]
            end_idx = label_indices[-1]

            # Aggiungi il numero di occorrenze al conteggio totale
            total_labels += len(label_indices)

            # Stampa l'intervallo
            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m (Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

        # Stampa il totale delle etichette per la condizione corrente
        print(f"\nTotale etichette (0 e 1): \033[1m{total_labels}\033[0m\n")

    return all_subj_data_by_coupled_cond


In [ ]:
# Parametri
conditions = ['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp',
              'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp']

prefix = "new_all_pt_concat_reconstructions_"
suffix = "_1_45"

# Chiamata alla funzione
new_concatenated_dictionaries_pt = concatenate_all_single_subj_coupled_experimental_conditions_pt(
    data_structure=new_subject_level_concatenations_coupled_exp_pt_1_45,
    conditions=conditions,
    prefix=prefix,
    suffix=suffix
)

# Stampa i risultati per verifica
print('\n\033[1mRISULTATO FINALE TUTTI I SOGGETTI TH\033[0m') 
for key, value in new_concatenated_dictionaries_pt.items():
    print(f"{key}:")
    print(f"  Dati: {value['data'].shape}")
    print(f"  Labels: {value['labels'].shape}")


#### STEP 6.3.2.1 - Salvataggio Dataset di **All Single Patients** EEG Preprocessed Data (1-45Hz) across **Couples of Experimental Conditions** INSIEME

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE_1_45

In [ ]:
new_concatenated_dictionaries_pt.keys()

In [ ]:
#Mi estraggo ogni sotto-dizionario

new_all_pt_concat_reconstructions_baseline_vs_th_resp_1_45 = new_concatenated_dictionaries_pt['new_all_pt_concat_reconstructions_baseline_vs_th_resp_1_45']

new_all_pt_concat_reconstructions_baseline_vs_pt_resp_1_45 = new_concatenated_dictionaries_pt['new_all_pt_concat_reconstructions_baseline_vs_pt_resp_1_45']

new_all_pt_concat_reconstructions_baseline_vs_shared_resp_1_45 = new_concatenated_dictionaries_pt['new_all_pt_concat_reconstructions_baseline_vs_shared_resp_1_45']

new_all_pt_concat_reconstructions_th_resp_vs_pt_resp_1_45 = new_concatenated_dictionaries_pt['new_all_pt_concat_reconstructions_th_resp_vs_pt_resp_1_45']
        
new_all_pt_concat_reconstructions_th_resp_vs_shared_resp_1_45 = new_concatenated_dictionaries_pt['new_all_pt_concat_reconstructions_th_resp_vs_shared_resp_1_45']

new_all_pt_concat_reconstructions_pt_resp_vs_shared_resp_1_45 = new_concatenated_dictionaries_pt['new_all_pt_concat_reconstructions_pt_resp_vs_shared_resp_1_45']

In [ ]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE'''
import pickle
   
base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#'BASELINE VS TH RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_baseline_vs_th_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_baseline_vs_th_resp_1_45, f)
                                  
#'BASELINE VS PT RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_baseline_vs_pt_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_baseline_vs_pt_resp_1_45, f)
        
#'BASELINE VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_baseline_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_baseline_vs_shared_resp_1_45, f)
    
#'TH RESP VS PT RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_th_resp_vs_pt_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_th_resp_vs_pt_resp_1_45, f)
        
#'TH RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_th_resp_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_th_resp_vs_shared_resp_1_45, f)
    
#'PT RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_pt_resp_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_pt_resp_vs_shared_resp_1_45, f)
    

### STEP 6.3.3 - All Single Patients EEG Preprocessed Data (1-45Hz) across **Triplets of Experimental Conditions**

#### Procedura

Per calcolare quante possibili triplette (combinazioni di 3 condizioni sperimentali) si possono formare da un insieme di 4 condizioni, utilizziamo il concetto di combinazioni senza ripetizione. La formula per il numero di combinazioni è:

C(n,k)=  k!⋅(n−k)! / n!

Dove:

- n è il numero totale di elementi nell'insieme (n = 4 in questo caso)
- k è il numero di elementi scelti (k = 3)


**Calcoliamo**:

C(4,3)= 4!/ 3⋅(4−3)! = 4⋅3⋅2⋅1 / (3⋅2⋅1)⋅1 = 4 

**Risultato**

Ci sono 4 possibili triplette che si possono formare dalle 4 condizioni sperimentali.

**Elenco delle Triplette**

Se vogliamo enumerarle:

['baseline', 'th_resp', 'pt_resp']
['baseline', 'th_resp', 'shared_resp']
['baseline', 'pt_resp', 'shared_resp']
['th_resp', 'pt_resp', 'shared_resp']

Queste sono tutte le combinazioni possibili

#### Implementazione

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE_1_45/

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/patients_data.pkl', 'rb') as f:
    patients_data = pickle.load(f)

In [ ]:
import itertools
import numpy as np

# Condizioni sperimentali
experimental_conditions = ['baseline', 'th_resp', 'pt_resp', 'shared_resp']

# Variabile di output
new_subject_level_concatenations_triplets_exp_pt_1_45 = {}

# Nuova variabile per tracciare il soggetto corrente stampato
last_subject_key = None

# Itera su ogni soggetto nella lista therapists_data
for subject_index, subject_data in enumerate(patients_data):
    subject_key = f'pt_{subject_index + 1}'  # Crea la chiave per il soggetto (es. 'th_1', 'th_2', ...)

    '''PER TRACCIARE SOGGETTO PRECEDENTE'''
    # Aggiungi separazione visiva quando cambia il soggetto
    if subject_key != last_subject_key:
        if last_subject_key is not None:  # Evita di stampare separatori prima del primo soggetto
            print("\n" + "-" * 50 + f" END OF {last_subject_key.upper()} " + "-" * 50 + "\n")
        print(f"\nProcessing Subject: {subject_key}\n" + "=" * 80)

    last_subject_key = subject_key  # Aggiorna il soggetto corrente

    # Inizializza il dizionario per questo soggetto
    new_subject_level_concatenations_triplets_exp_pt_1_45[subject_key] = {}

    '''Creo un suffisso dinamico per:
    1) Estrazione dei dati di una condizione sperimentale di un certo soggetto 
    (i.e., baseline_1 dove "_1" è il suffisso)
    2) Estrazione delle labels di una condizione sperimentale di un certo soggetto 
    (i.e., baseline_1_labels dove "_1_labels" è il suffisso)
    '''
    # Suffisso dinamico basato sull'indice del soggetto
    data_suffix = f"_{subject_index + 1}"
    labels_suffix = f"{data_suffix}_labels"

    # Crea tutte le combinazioni uniche di triplette di condizioni sperimentali
    condition_triplets = list(itertools.combinations(experimental_conditions, 3))

    # Loop su tutte le combinazioni di triplette
    for cond_1, cond_2, cond_3 in condition_triplets:
        condition_triplet_key = f"{cond_1}_vs_{cond_2}_vs_{cond_3}"  # Nome della combinazione

        # Stampa il messaggio per la triplette corrente
        print(f"\n\t\tCreation of Triplet Condition \033[1m{condition_triplet_key}\033[0m")

        # Estrai i dati e le etichette per le tre condizioni
        data_cond_1 = subject_data.get(f"{cond_1}{data_suffix}")
        print(f"Extracting data_cond_1 which is {cond_1}{data_suffix}")
        labels_cond_1 = subject_data.get(f"{cond_1}{labels_suffix}")
        print(f"Extracting labels_cond_1 which is {cond_1}{labels_suffix}")

        data_cond_2 = subject_data.get(f"{cond_2}{data_suffix}")
        print(f"Extracting data_cond_1 which is {cond_2}{data_suffix}")
        labels_cond_2 = subject_data.get(f"{cond_2}{labels_suffix}")
        print(f"Extracting labels_cond_1 which is {cond_2}{labels_suffix}")

        data_cond_3 = subject_data.get(f"{cond_3}{data_suffix}")
        print(f"Extracting data_cond_1 which is {cond_3}{data_suffix}")
        labels_cond_3 = subject_data.get(f"{cond_3}{labels_suffix}")
        print(f"Extracting labels_cond_1 which is {cond_3}{labels_suffix}")
        
        # Verifica che i dati e le etichette siano validi
        #if any(x is None for x in [data_cond_1, labels_cond_1, data_cond_2, labels_cond_2, data_cond_3, labels_cond_3]):
        #    print(f'PROBLEM FOR THE SUBJECT {subject_index}')  
        #else: 
        #    continue # Salta se manca qualcosa

        # Converti le etichette da lista a numpy array con valori univoci per ciascuna condizione
        labels_cond_1 = np.zeros(len(labels_cond_1), dtype=int)  # Etichette di cond_1 come 0
        labels_cond_2 = np.ones(len(labels_cond_2), dtype=int)   # Etichette di cond_2 come 1
        labels_cond_3 = np.full(len(labels_cond_3), 2, dtype=int)  # Etichette di cond_3 come 2

        # Concatenazione dei dati e delle etichette
        concatenated_data = np.vstack((data_cond_1, data_cond_2, data_cond_3))
        concatenated_labels = np.hstack((labels_cond_1, labels_cond_2, labels_cond_3))

        # Salva i dati concatenati nella struttura
        new_subject_level_concatenations_triplets_exp_pt_1_45[subject_key][condition_triplet_key] = {
            'data': concatenated_data,
            'labels': concatenated_labels
        }

        # Dopo aver trattato tutti i livelli, aggiungi una separazione visiva per il soggetto
        print("-" * 50 + f"-" * 50)

        

In [ ]:
# Itera su ogni soggetto nel dizionario delle triplette
print("\n\033[1mIndicizzazione dei dati e delle etichette per ogni sotto-tripletta di condizioni sperimentali:\033[0m\n")

for subject_key, triplets_data in new_subject_level_concatenations_triplets_exp_pt_1_45.items():
    print(f"\nSoggetto: \033[1m{subject_key}\033[0m")
    print("=" * 80)

    for triplet_key, triplet_data in triplets_data.items():
        print(f"\nTripletta: \033[1m{triplet_key}\033[0m")
        
        # Estrai i dati e le etichette
        concatenated_data = triplet_data['data']
        concatenated_labels = triplet_data['labels']
        
        # Conta le etichette uniche
        unique_labels = np.unique(concatenated_labels)
        
        # Variabile per il conteggio totale
        total_samples = 0
        
        for label in unique_labels:
            # Trova gli indici corrispondenti a questa etichetta
            label_indices = np.where(concatenated_labels == label)[0]
            
            # Determina l'intervallo di indici
            start_idx = label_indices[0]
            end_idx = label_indices[-1]
            
            # Aggiungi il numero di campioni al totale
            total_samples += len(label_indices)
            
            # Stampa le informazioni sull'etichetta
            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m (Totale: {len(label_indices)})")
        
        # Verifica il totale dei campioni
        print(f"\nTotale campioni: \033[1m{total_samples}\033[0m")
        print("-" * 80)

In [ ]:
!pwd

In [ ]:
'''PER SALVARE STRUTTURA DATI E LABEL OGNI SOGGETTO NON ANCORA CONCATENATI TRA DI LORO

PS: viene comunque già salvato in  --> new_subject_level_concatenations_triplets_exp_th_1_45 '''

import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Salva il dizionario th_data_dict in un file pkl
with open(f'{base_path}/new_subject_level_concatenations_triplets_exp_pt_1_45.pkl', 'wb') as file:
    pickle.dump(new_subject_level_concatenations_triplets_exp_pt_1_45, file)


### STEP 6.3.3.1 - Mi concanteno All Single Patients EEG Preprocessed Data (1-45Hz) across **Triplets of Experimental Conditions**

In [ ]:
# Caricare l'intero dizionario annidato con pickle
import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_subject_level_concatenations_triplets_exp_pt_1_45.pkl', 'rb') as f:
    new_subject_level_concatenations_triplets_exp_pt_1_45 = pickle.load(f)

In [ ]:
#new_subject_level_concatenations_triplets_exp_th_1_45.keys()
new_subject_level_concatenations_triplets_exp_pt_1_45['pt_1'].keys()

In [ ]:
new_subject_level_concatenations_triplets_exp_pt_1_45['pt_1']['baseline_vs_th_resp_vs_pt_resp'].keys()

In [ ]:
# Itera attraverso ogni soggetto nel dizionario
for i, subject_data in new_subject_level_concatenations_triplets_exp_pt_1_45.items():
    print(f"Soggetto {i}:")
    print("Chiavi presenti:", list(subject_data.keys()))
    print("-" * 50)

In [ ]:

def concatenate_all_single_subj_tripled_experimental_conditions_pt(data_structure, conditions, prefix, suffix):
    
    """
    Concatena i dati e le etichette per ogni condizione sperimentale da una struttura dati con un livello in più,
    ordinandoli anche per etichetta.

    Parameters:
        data_structure (dict): La struttura dati di input che contiene i dati per soggetti e condizioni.
        conditions (list): Le condizioni sperimentali (chiavi del secondo livello) da processare.
        prefix (str): Il prefisso del nome dinamico del dizionario.
        suffix (str): Il suffisso del nome dinamico del dizionario.

    Returns:
        dict: Un dizionario contenente i nuovi dizionari con i dati concatenati e le etichette per ogni condizione.
    """
    
    #Questo conterrà i dati complessivi di tutti i soggetti per ogni coppia di condizioni sperimentali
    all_subj_data_by_coupled_cond = {}

    # Itera su ogni condizione sperimentale
    for condition_triplet in conditions:
        
        # Dizionari per raccogliere dati e labels ordinati per ogni coppia di condizioni sperimentali
        # che è dinamico, per ogni coppia di condizioni sperimentali 
        
        #(quindi si ricreeranno passando alla condizione sperimentale successiva!)
        
        
        #print(f"Creo dizionari di dati e labels per la condizione:")
        #print(f"\n{condition_triplet}")
        data_by_label = {}
        labels_by_label = {}
        
        
        # Lista temporanea per salvare la shape delle etichette per ogni soggetto per ogni etichetta iterata
        
        '''
        Per ogni condizione sperimentale, per ognuna delle 2 labels, 
        la shape delle etichette per ogni soggetto, 

        e me le salvi dentro una lista temporanea, che salva in formato la shape (solo il valore numerico) di ogni soggetto 
        per l'etichette iterata per quella condizione sperimentale là.

        poi, a questo livello dei print 

         # **Print finale per verificare la concatenazione per ogni label**
            print(f"Condizione: {condition_triplet}, Etichetta: {label}")
            print(f"  - Shape dei dati concatenati per {label}: {concatenated_data_by_label[label].shape}")
            print(f"  - Shape delle etichette concatenate per {label}: {concatenated_labels_by_label[label].shape}")

        vorrei che mi stampassi anche questa lista alla fine del print, di modo che possa vedere visivamente subito il numero di labels di ogni soggetto associate a quella labels iterata là così da vedere se il conteggio corrisponde visivamente al totale salvate dentro 

        "concatenated_data_by_label[label]"
        '''
        
        shape_labels_per_subject = {0: [], 1: [], 2: []}  # Inizializza un dizionario per le etichette 0 e 1


        # Itera su tutti i soggetti
        # In questo caso, itera sulle chiavi di ogni soggetto
        
        # Quindi prenderà, per la relativa coppia di condizioni sperimentali di ogni soggetto,
        # i dati e le labels di quel soggetto, per quella relativa coppia di condizioni sperimentali
        
        for subject_key in data_structure.keys():
            
            #print(subject_key)
            #print(data_structure.keys())
            
            # Qui estrae i dati e le labels per questa condizione sperimentale di quel soggettio lì
            subject_data = data_structure[subject_key][condition_triplet]['data']
            subject_labels = data_structure[subject_key][condition_triplet]['labels']

            # Trova le etichette uniche e gli indici corrispondenti per quella coppia di condizioni sperimentali lì,
            # Ossia, potrà trovare gli 0 e gli 1 
            
            unique_labels = np.unique(subject_labels)
        
            #A quel punto, per ognuna delle due labels trovate per quella coppia di condizioni sperimentali lì
            #Che saranno sempre o 0 o 1 
            
            for label in unique_labels:
                
                # Trova gli indici dei dati corrispondenti a questa etichetta
                # Una volta per lo 0 ed una volta per l' 1
                
                label_indices = np.where(subject_labels == label)[0]

                # A quel punto, estrae i dati e le labels per questi indici
                # Una volta per lo 0 ed una volta per l' 1
                
                data_for_label = subject_data[label_indices]
                labels_for_label = subject_labels[label_indices]

                # A quel punto, per ogni soggetto, per ogni condzione sperimentale, 
                # per quelle due labels là (sempre presenti, per ogni coppia di condizioni sperimentali)
                # Una volta per lo 0 ed una volta per l' 1
                
                #Andrà a creare per ogni etichetta, una chiave che si chiamerà 
                #o 0 od 1 (inizialmente, vuoto -> perché deve esser inizializzato)
                #E poi, dopo, ci appenderà le labels 
                 # Una volta per lo 0 ed una volta per l' 1
                #  Di quel soggetto per quella coppia di condizioni sperimentali iterate a quel momento
                
                #Aggiunge ai dizionari globali, creando la chiave se non esiste
                if label not in data_by_label:
                    data_by_label[label] = []
                    labels_by_label[label] = []

                data_by_label[label].append(data_for_label)
                labels_by_label[label].append(labels_for_label)
                
                 # **Salva la shape delle etichette per il soggetto corrente**
                shape_labels_per_subject[label].append(labels_for_label.shape[0])  # Aggiungi solo la dimensione (numero di etichette)

        
                # **Aggiungi un print di controllo per ogni soggetto**
                print(f"Soggetto: \033[1m{subject_key}\033[0m, Condizione: \033[1m{condition_triplet}\033[0m, Etichetta: \033[1m{label}\033[0m, Shape: \033[1m{labels_for_label.shape[0]}\033[0m")
                #print(f"  - Numero di \033[1mdati\033[0m per {label}: {data_for_label.shape[0]}")
                #print(f"  - Numero di \033[1metichette\033[0m per {label}: {labels_for_label.shape[0]}")
                
                    
        # Dopodiché, vado a creare invece i dizionari che conterranno
        # Le concatenazioni, di dati e labels corrispondenti, di tutti i soggetti per cui l'etichetta era 
        # o 0 od 1 
        
        # Di conseguenza, qui dentro dovrei avere, per ogni coppia di condizioni sperimentali
        # Tutti gli 0 ed 1 (ed i relativi dati corrispondenti)
        # di tutti i soggetti, ma concatenati
        
        
        concatenated_data_by_label = {}
        concatenated_labels_by_label = {}

        for label in data_by_label.keys():
            concatenated_data_by_label[label] = np.vstack(data_by_label[label])
            concatenated_labels_by_label[label] = np.hstack(labels_by_label[label])
            
            # **Calcolare la shape totale delle etichette**
            #total_labels_0 = np.sum(1 for subject_labels in labels_by_label[label] if 0 in subject_labels)
            #total_labels_1 = np.sum(1 for subject_labels in labels_by_label[label] if 1 in subject_labels)
            #total_labels = total_labels_0 + total_labels_1

            # **Determinare gli indici delle etichette 0 e 1 nell'array finale**
            
            # Gli indici delle etichette 0
            indices_labels_0 = np.where(concatenated_labels_by_label[label] == 0)[0]
            
            # Gli indici delle etichette 1
            indices_labels_1 = np.where(concatenated_labels_by_label[label] == 1)[0]
            
            # Gli indici delle etichette 2
            indices_labels_2 = np.where(concatenated_labels_by_label[label] == 2)[0]
            
            # Indici iniziale e finale per le etichette 0 e 1
            start_idx_0 = indices_labels_0[0] if len(indices_labels_0) > 0 else None
            end_idx_0 = indices_labels_0[-1] if len(indices_labels_0) > 0 else None
            
            start_idx_1 = indices_labels_1[0] if len(indices_labels_1) > 0 else None
            end_idx_1 = indices_labels_1[-1] if len(indices_labels_1) > 0 else None
            
            start_idx_2 = indices_labels_2[0] if len(indices_labels_2) > 0 else None
            end_idx_2 = indices_labels_2[-1] if len(indices_labels_2) > 0 else None
    
    
            # **Print finale per verificare la concatenazione per ogni label**
            #print(f"\nCondizione: \033[1m{condition_triplet}\033[0m, Etichetta: {label}")
            #print(f"  - Shape dei dati concatenati per \033[1m{label}\033[0m: {concatenated_data_by_label[label].shape}")
            #print(f"  - Shape delle etichette concatenate per \033[1m{label}\033[0m: {concatenated_labels_by_label[label].shape}")
            
            # **Stampa la lista delle shapes delle etichette per ogni soggetto per questa etichetta**
            #print(f"\n  - Shape delle etichette per soggetto (per etichetta {label}): {shape_labels_per_subject[label]}\n")

            
            # **Stampa il conteggio totale delle etichette**
            #print(f"\n  - Totale delle etichette 0: {total_labels_0}")
            #print(f"  - Totale delle etichette 1: {total_labels_1}")
            #print(f"  - Totale delle etichette per la condizione: {total_labels}\n")

            # **Stampa gli indici per le etichette 0 e 1**
            # **OSSIA --> Stampa gli indici per l'etichetta corrente**
            
            #if label == 0:
            #    print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #else:
            #    print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}\n")

    
            #print(f"\n  - Indici per etichetta 0: Inizio = {start_idx_0}, Fine = {end_idx_0}")
            #print(f"  - Indici per etichetta 1: Inizio = {start_idx_1}, Fine = {end_idx_1}")

    
        #ARRIVATI FINO A QUI, abbiamo che siccome stiamo iterando prima per tutti gli 0 e poi per tutti gli 1
        #Significa che, assumendo che siamo dentro 'baseline_vs_th_resp' e che 
        
        #'baseline' sia rappresentato dalle etichette 0
        #'th_resp' sia rappresentato dalle etichette 1
        
        #Al PRIMO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'baseline' per 'baseline_vs_th_resp'di tutti i soggetti)
        
        #Al SECONDO ciclo avrò che:
        
        #con concatenated_data_by_label[label] ho solo concatenato tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        #con concatenated_labels_by_label[label] ho solo concatenato tutti gli 0 (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #Quindi mi manca ancora 
        
        #A) CONCATENARE I DATI:
        
        #1)prima tutti i dati (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti i dati (di 'th_resp' per 'baseline_vs_th_resp'  di tutti i soggetti)
        
        #che verrà fatto dentro all_data (che è anch'esso una variabile dinamica!)
        
        #B) CONCATENARE LE LABELS:
        
        #1)prima tutti le labels (di 'baseline' per 'baseline_vs_th_resp' di tutti i soggetti) 
        
        #CON
        
        #2)tutti le labels (di 'th_resp' per 'baseline_vs_th_resp' di tutti i soggetti)
        
        #che verrà fatto dentro all_labels (che è anch'esso una variabile dinamica!)
        
        # Liste per raccogliere dati e labels di tutte le etichette
        
        # Qui dentro, invece, dov con
        all_data = []
        all_labels = []

        for label in concatenated_data_by_label.keys():
            all_data.append(concatenated_data_by_label[label])
            all_labels.append(concatenated_labels_by_label[label])
        
        
        #Alla fine, qui dentro avrò che, PER OGNI COPPIA DI CONDIZIONI SPERIMENTALI
        
        
        #'final_data' dovrebbe avere 
            #- prima tutti i dati di tutti i soggetti associati all'etichetta 0 
            #- e poi tutti i dati di tutti i soggetti associati all'etichetta 1
        
        #'final_labels' dovrebbe avere 
            #- prima tutte le labels di tutti i soggetti associati all'etichetta 0
            #- e poi tutte tutte le labels di tutti soggetti associati all'etichetta 1...

        
        # Concatenazione finale per la condizione corrente
        final_data = np.vstack(all_data)
        final_labels = np.hstack(all_labels)
    
        
        # Nome dinamico del dizionario
        dict_name = f"{prefix}{condition_triplet}{suffix}"

        # Salva il risultato nel dizionario globale
        all_subj_data_by_coupled_cond[dict_name] = {
            'data': final_data,
            'labels': final_labels
        }
        
    # Dopo aver costruito tutti i sotto-dizionari, iterare per stampare gli intervalli
    print("\n\033[1mIntervalli di indici per ciascuna etichetta nei sotto-dizionari:\033[0m\n")

    for cond_key, cond_data in all_subj_data_by_coupled_cond.items():
        print(f"Condizione: \033[1m{cond_key}\033[0m\n")

        # Estrai le etichette dal sotto-dizionario
        labels = cond_data['labels']

        # Conta le etichette uniche
        unique_labels = np.unique(labels)

        # Variabile per il conteggio totale delle etichette
        total_labels = 0

        # Stampa gli intervalli di indici per ciascuna etichetta
        for label in unique_labels:

            # Trova gli indici corrispondenti a questa etichetta
            label_indices = np.where(labels == label)[0]

            # Determina l'intervallo
            start_idx = label_indices[0]
            end_idx = label_indices[-1]

            # Aggiungi il numero di occorrenze al conteggio totale
            total_labels += len(label_indices)

            # Stampa l'intervallo
            print(f"  Etichetta \033[1m{label}\033[0m: Indici \033[1m{start_idx}-{end_idx}\033[0m (Totale Etichette: \033[1m{len(label_indices)}\033[0m)")

        # Stampa il totale delle etichette per la condizione corrente
        print(f"\nTotale etichette (0, 1 e 2): \033[1m{total_labels}\033[0m\n")

    return all_subj_data_by_coupled_cond

In [ ]:
# Parametri

#baseline_vs_th_resp_vs_pt_resp
#baseline_vs_th_resp_vs_shared_resp
#baseline_vs_pt_resp_vs_shared_resp
#th_resp_vs_pt_resp_vs_shared_resp

conditions = ['baseline_vs_th_resp_vs_pt_resp', 'baseline_vs_th_resp_vs_shared_resp','baseline_vs_pt_resp_vs_shared_resp', 'th_resp_vs_pt_resp_vs_shared_resp']

prefix = "new_all_pt_concat_reconstructions_"
suffix = "_1_45"

tripled_conditions = list(new_subject_level_concatenations_triplets_exp_pt_1_45['pt_1'].keys())

# Chiamata alla funzione
new_concatenated_dictionaries_pt = concatenate_all_single_subj_tripled_experimental_conditions_pt(
    data_structure=new_subject_level_concatenations_triplets_exp_pt_1_45,
    conditions=tripled_conditions,
    prefix=prefix,
    suffix=suffix
)

# Stampa i risultati per verifica
print('\n\033[1mRISULTATO FINALE TUTTI I SOGGETTI TH\033[0m') 
for key, value in new_concatenated_dictionaries_pt.items():
    print(f"{key}:")
    print(f"  Dati: {value['data'].shape}")
    print(f"  Labels: {value['labels'].shape}")


#### STEP 6.3.3.2 - Salvataggio Dataset di **All Single Patients** EEG Preprocessed Data (1-45Hz) across **Triplets of Experimental Conditions** INSIEME

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE_1_45

In [ ]:
new_concatenated_dictionaries_pt.keys()

In [ ]:
#Mi estraggo ogni sotto-dizionario

new_all_pt_concat_reconstructions_baseline_vs_th_resp_vs_pt_resp_1_45 = new_concatenated_dictionaries_pt['new_all_pt_concat_reconstructions_baseline_vs_th_resp_vs_pt_resp_1_45']

new_all_pt_concat_reconstructions_baseline_vs_th_resp_vs_shared_resp_1_45 = new_concatenated_dictionaries_pt['new_all_pt_concat_reconstructions_baseline_vs_th_resp_vs_shared_resp_1_45']

new_all_pt_concat_reconstructions_baseline_vs_pt_resp_vs_shared_resp_1_45 = new_concatenated_dictionaries_pt['new_all_pt_concat_reconstructions_baseline_vs_pt_resp_vs_shared_resp_1_45']

new_all_pt_concat_reconstructions_th_resp_vs_pt_resp_vs_shared_resp_1_45 = new_concatenated_dictionaries_pt['new_all_pt_concat_reconstructions_th_resp_vs_pt_resp_vs_shared_resp_1_45']


In [ ]:
''' PATH  --> cd New_Plots_Sliding_Estimator_MNE_1_45'''
import pickle
   
base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_1_45/'

#'BASELINE VS TH RESP VS PT RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_baseline_vs_th_resp_vs_pt_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_baseline_vs_th_resp_vs_pt_resp_1_45, f)
                                  
#'BASELINE VS TH RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_baseline_vs_th_resp_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_baseline_vs_th_resp_vs_shared_resp_1_45, f)
        
#'BASELINE VS PT RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_baseline_vs_pt_resp_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_baseline_vs_pt_resp_vs_shared_resp_1_45, f)
    
#'TH RESP VS PT RESP VS SHARED RESP'
# Salvare l'intero dizionario annidato con pickle
with open(f'{base_path}/new_all_pt_concat_reconstructions_th_resp_vs_pt_resp_vs_shared_resp_1_45.pkl', 'wb') as f:
    pickle.dump(new_all_pt_concat_reconstructions_th_resp_vs_pt_resp_vs_shared_resp_1_45, f)


## **Logistic Regression**

##### **Parametri version 1.0.5 (stable)**: https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LogisticRegression.html#sklearn.linear_model.LogisticRegression

#### **ALL SINGLE Therapists (TH01-TH20)**

#### Automatization of all steps from: 

1) "**subject_level_concatenations_th**" : ricostruzioni 4 e 5° livello wavelet da approx coefficients
2) "**new_subject_level_concatenations_th**":  ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_th_1_20**": EEG preprocessed signal filtered 1-20Hz 

In [ ]:
!pwd

In [ ]:
cd Interrogait

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''


#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
#    new_subject_level_concatenations_th = pickle.load(f)
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle
import numpy as np

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    

#PER SALVARE I FILE
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('NOME DEL FILE.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations, f)


#subject_level_concatenations_th['th_1'].keys()

In [ ]:
new_subject_level_concatenations_th.keys()

In [ ]:
np.unique(new_subject_level_concatenations_th['th_16']['labels'],return_counts=True)

In [ ]:
#new_subject_level_concatenations_th.keys()

#dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 
#           'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

new_subject_level_concatenations_th['th_16'].keys()
#dict_keys(['theta', 'delta', 'theta_strict', 'labels'])

In [ ]:
new_subject_level_concatenations_th_1_20['th_16'].keys()

##### **Descrizione degli step nel codice per ottenere e salvare nelle paths le best score performances per il level 4 e 5 dalle ricostruzioni**:

Vorrei in questo caso, per velocizzare, iterare su 

subject_level_concatenations, che ha questa struttura...

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


al cui interno ha per ogni chiave di primo ordine, un altro dizionario annidato, che è fatto di queste chiavi


dict_keys(['theta', 'delta', 'labels'])

dentro 'theta' e 'delta' ci sono tutti i dati di tutte le condizioni sperimentali del singolo soggetto

del tipo 'theta' o 'delta' conterrà un array con shape

(204, 3, 300)

con 1° dimensione i trial, poi i canali, poi i punti di ogni trial (campioni EEG)

e dentro 'labels' ho invece l'array delle labels concatenate...
(204,)


<br>


Ora però, vorrei che ... 

Se ad esempio nel soggetto 'th_1' entri nella chiave 'theta', 

allora poi il file corrispondente .txt deve essere scritto con una path dinamica, che cambia a seconda 
- sia del soggetto iterato
- sia del livello di ricostruzione dei dati

Ossia:

la "params_dir" è fissa

mentre 

"params_file_path" è dinamica, e cambia a seconda del soggetto iterato e del livello. 

Per cui sarà una composizione di stringhe fisse e stringhe 'mobili', ossia

'params_file_path' = 'optimized_params_' + {subject} dove subject dovrebbe essere una lista di stringhe che si preleva dalle chiavi di primo ordine di "subject_level_concatenations" che erano

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


seguito da "_level_{level}_std" dove {level} dipende dal nome della chiave del sotto-dizionario iterato per ogni soggetto...

Ossia, ad esempio dentro il sotto-dizionario del primo soggetto di "subject_level_concatenations" cioè

subject_level_concatenations['th_1'], 

Se la sua sotto-chiave è 'theta' allora il level = 4, se la chiave è 'delta' allora il level = 5, 



Quindi la costruzione finale della path dinamica del file specifico per il soggetto 1 deve essere

 
params_file_path = 'optimized_params_' +'{subject}' + "_level_{level}_std.txt"

e sarà se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_1' + "_level_4_std.txt"


e sarà se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_1' + "_level_5_std.txt"


in questo modo, farei un loop unico su tutte le sottochiavi dei dizionari annidati dentro 
"subject_level_concatenations" 

ossia 
dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

e per ognuno vedo se la sua sotto-chiave sarà 'theta' o 'delta' e creerà dei file .txt corrispondenti nella param_dir che gli ho chiesto...

Il resto del codice non toccarlo invece, perché dovrebbe creare dei file .txt per ogni soggetto per ogni livello di ricostruzione dei dati,
e salverà le analisi nel file .txt corrispondente



Ad esempio, continuando col soggetto 2:

la costruzione finale della path dinamica del file specifico per il soggetto 2

Sarà, se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_2' + "_level_4_std.txt"


e sarà, se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_2' + "_level_5_std.txt"


e così via per tutti gli altri soggetti




##### **ALL SINGLE Therapists (TH01-TH16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DALLE RICOSTRUZIONI**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**


In [ ]:
new_subject_level_concatenations_th.keys()

In [ ]:
''' THERAPISTS!

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ, Θ, δ e Θ strict!)


******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* *******
#DIRECTORY PATH MESSA INIZIALMENTE  

# -->>>>> /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/prova/ <<<<<--

#PER NON SOVRASCRIVERE RISULTATI RANDOM SEARCH SU TUTTI I SOGGETTI CON LOGISTIC REGRESSION!!!!!

******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* *******


Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare

#Some penalties may not work with some solvers. 
#See the parameter solver below, to know the compatibility between the penalty and solver.


Per la classificazione multi-classe con l'opzione multi_class='multinomial', 
puoi utilizzare i seguenti solver e le relative penalità:

newton-cg: supporta solo l2 e None.
sag: supporta solo l2 e None.
saga: supporta l1, l2, elasticnet, e None.
lbfgs: supporta solo l2 e None.

Quindi, se vuoi esplorare solo il caso multinomiale, puoi utilizzare i seguenti abbinamenti di solver e penalità:

newton-cg: l2, None
sag: l2, None
saga: l1, l2, elasticnet, None
lbfgs: l2, None

'''

import numpy as np
import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER MULTINOMIAL LOGISTIC REGRESSION'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra penalty e solver, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...


# Definizione dei parametri validi, ossia delle coppie solver-penalty associate
params = {'newton-cg': ['l2', None],
    'sag': ['l2', None],
    'saga': ['l1', 'l2', 'elasticnet', None],
    'lbfgs': ['l2', None]
}


# Assicuriamoci di non avere duplicati e di avere una lista di dizionari separati per solver e penalty
parameters_dist = {
    'solver': list(params.keys()),
    'penalty': list(set(penalty for penalties in params.values() for penalty in penalties)),
    'C': [0.001, 0.01, 0.1, 1, 10, 100]
    
}

print(f"\033[1mparameters_dist\033[0m è: {parameters_dist}")

def generate_valid_params(params):
    valid_params = []
    
    # Generate values from 0 to 1 (inclusive) with step 0.05
    l1_ratio_values = np.append(np.arange(0.0, 1.0, 0.05), 1.0)

    # Impongo parametro C con valori su scala logaritmica 
    C_values = [0.001, 0.01, 0.1, 1, 10, 100]

    for C in C_values: 
        for solver in params['solver']:
            if solver == 'newton-cg':
                penalties = ['l2', None]
            elif solver == 'sag':
                penalties = ['l2', None]
            elif solver == 'lbfgs':
                penalties = ['l2', None]
            elif solver == 'saga':
                penalties = ['l1', 'l2', 'elasticnet', None]  # Include None here explicitly
            else:
                penalties = params['penalty']
            
            # Create parameter dictionaries for each combination of solver and penalty
            for penalty in penalties:
                if penalty == 'elasticnet':
                    for l1_ratio in l1_ratio_values:
                        valid_params.append({'solver': [solver], 'penalty': ['elasticnet'], 'l1_ratio': [l1_ratio], 'C': [C]})
                        
                else:
                    valid_params.append({'solver': [solver], 'penalty': [penalty], 'C': [C]})
    
    return valid_params


# Funzione per verificare se una combinazione di iperparametri è valida
def valid_param_combination(params):
    solver = params['solver']
    penalty = params['penalty']
    
    if solver in ['newton-cg', 'lbfgs', 'sag'] and penalty in ['l2', None]:
        return True
    elif solver == 'saga' and penalty in ['l1', 'l2', 'elasticnet', None]:
        return True
    else:
        return False

valid_params_list = generate_valid_params(parameters_dist)
print(f"\n\033[1mvalid_params_list\033[0m è: {valid_params_list}")




# Itera attraverso i soggetti

'''OLD VERSION'''
#for subject, levels in subject_level_concatenations.items():

'''NEW VERSION'''
for subject, levels in new_subject_level_concatenations_th.items():
    
    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO'''
    
    #if subject == 'th_17' or subject == 'th_18' or subject == 'th_19':
    if subject == 'th_20':

        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")


        '''NEW VERSION'''
        #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
        params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params'

        # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
        #                                      'delta' = δ,i.e., approx_5 ,
        #                                      'theta_strict' = Θ, i.e., detail_5,
        #                                      'labels') 

        for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'


            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")

            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_std.txt'

            #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\t\033[1m{params_dir}\033[0m"),
            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

            y = levels['labels'] # Estraiamo le labels livello corrente del soggetto corrente

            '''OLD VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            #params_dir = '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/prova'

            #FILE PATH DINAMICA PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            #A SECONDA DEL SOGGETTO E LIVELLO DI RICOSTRUZIONE DEI DATI PRESI IN ESAME 

            # Costruzione del percorso del file in maniera dinamica
            #params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_std.txt'

            #if not os.path.exists(params_dir):
            #    os.makedirs(params_dir)

            #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\t\033[1m{params_dir}\033[0m"),
            #print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE LOGISTIC REGRESSION

            # Inizializzo modello Logistic Regression base (da sklearn.LinearModel version 1.0.5)
            log_reg_base = LogisticRegression(class_weight = class_weight_dict, max_iter = 20000)

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni istante temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0


            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")


            '''INIZIALIZZAZIONE RANDOM SEARCH'''

            # Inizializzazione della Random Search:

            #https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

            #cv: int, cross-validation generator or an iterable, default=None
            #Determines the cross-validation splitting strategy. 

            #Possible inputs for cv are:

            #None, to use the default 5-fold cross validation,
            #integer, to specify the number of folds in a (Stratified)KFold,
            #CV splitter,
            #An iterable yielding (train, test) splits as arrays of indices.

            #random_state: int, RandomState instance or None, default=None
            #Pseudo random number generator state used for random uniform sampling from lists of possible values 
            #instead of scipy.stats distributions. Pass an int for reproducible output across multiple function calls

            # RandomizedSearchCV è una tecnica di ricerca iperparametrica che 
            # campiona casualmente combinazioni di iperparametri da un insieme predefinito.

            #n_iter determina il numero di combinazioni di iperparametri da testare durante la ricerca


            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1



            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                #print(X_window_reshaped.shape)

                #Da https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

                #param_distributions: 

                #Dictionary with parameters names (str) as keys and distributions or lists of parameters to try. 
                #Distributions must provide a rvs method for sampling (such as those from scipy.stats.distributions). 
                #If a list is given, it is sampled uniformly. 
                #If a list of dicts is given, first a dict is sampled uniformly, 
                #and then a parameter is sampled using that dict as above.

                try:
                    rand_search = RandomizedSearchCV(
                        estimator = log_reg_base,
                        param_distributions = valid_params_list,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )
                    #random_state = 42 + window_start  # Corretto random_state


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_reshaped, y)

                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Controlla le combinazioni testate e conta quelle valide
                    #valid_combinations_count = 0

                    # Controlla le combinazioni testate
                    print(f"\n\033[1mValid hyperparameter combinations tested for n_window {window_start}-{window_end}\033[0m:\n")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:
                        for i, params in enumerate(rand_search.cv_results_['params']):
                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"Window {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n")

                        for params in rand_search.cv_results_['params']:
                            if valid_param_combination(params):
                                valid_combination_count += 1
                                print(f"\033[1mSolver\033[0m: {params['solver']}, \033[1mPenalty\033[0m: {params['penalty']}, \033[1mC\033[0m: {params['C']}", end = '')
                                if 'l1_ratio' in params:
                                    print(f", \033[1ml1_ratio\033[0m: {params['l1_ratio']}")
                                else:
                                    print()
                            else:
                                invalid_combination_count += 1
                                print(f"Invalid combination found: {params}")

                            #QUI

                        # Ottieni il modello con i migliori iper-parametri:

                        #Questa variabile ti restituisce il set di iper-parametri che ha prodotto il miglior punteggio 
                        #(migliore accuratezza) durante la Randomized Search per la finestra corrente. 
                        #È un dizionario che specifica valori come il solver, la penalizzazione, e altri iper-parametri.

                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                        #Questa variabile ti restituisce il punteggio (accuracy) del modello che ha ottenuto le migliori prestazioni 
                        #con i parametri in rand_search.best_params_. 
                        #Rappresenta la misura delle performance del modello sui dati di validazione durante la Randomized Search.

                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Stampa i risultati per la finestra corrente
                        #print(f"\033[1mWindow {window_start}-{window_end}\033[0m: Best Params = {best_model_params}, Best Score = {best_score}")

                    # Salva i parametri migliori per la finestra temporale corrente in una riga del file di testo
                    #with open(params_file_path, 'a') as f:
                    #    f.write(f"Window n° {time_point}\t{json.dumps(best_model_params)}\n")

                        # Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:
                    print(f"An error occurred for window {window_start}-{window_end}: {e}")
                    invalid_combination_count += 1

                    # Continua con l'iterazione successiva senza interrompere l'intero loop

                # Memorizza il tempo di fine per il punto temporale corrente
                time_point_end = time.time()

                # Calcola il tempo di esecuzione per il punto temporale corrente
                time_point_elapsed = time_point_end - time_point_start

                # Aggiungi il tempo di esecuzione alla lista
                execution_times.append(time_point_elapsed)

                # Stampa i risultati per il punto temporale corrente
                #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                print()
                print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds")
                print()


            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            print()
            print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                        f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                else:
                    f.write("No valid windows found in the specified range.\n")

                f.write('\n')
                f.write(f"Total execution time: {total_execution_time} seconds\n")
                f.write(f"Number of valid combinations: {valid_combination_count}\n")
                f.write(f"Number of invalid combinations: {invalid_combination_count}\n")

##### **ALL SINGLE Therapists (TH01-TH16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

- **EEG preprocessed signal**: filtered 1-20

In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun soggetto nel dizionario
for soggetto, dati in new_subject_level_concatenations_th_1_20.items():
    
    # Verifica che 'data' sia presente tra le chiavi
    if 'data' in dati:
        
        # Sotto-seleziona i canali di interesse
        dati_originali = dati['data']  # Estrai i dati
        
        dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali

        # Aggiorna la chiave 'data' con i dati filtrati
        new_subject_level_concatenations_th_1_20[soggetto]['data'] = dati_sottoselezionati

        # Opzionale: stampa di controllo per verificare la nuova forma dei dati
        print(f"Soggetto {soggetto}: {dati_sottoselezionati.shape}")

In [ ]:
##### **ALL SINGLE Therapists (TH01-TH15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DAL SEGNALE 1-20Hz**

import numpy as np
import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER MULTINOMIAL LOGISTIC REGRESSION'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra penalty e solver, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...


# Definizione dei parametri validi, ossia delle coppie solver-penalty associate
params = {'newton-cg': ['l2', None],
    'sag': ['l2', None],
    'saga': ['l1', 'l2', 'elasticnet', None],
    'lbfgs': ['l2', None]
}


# Assicuriamoci di non avere duplicati e di avere una lista di dizionari separati per solver e penalty
parameters_dist = {
    'solver': list(params.keys()),
    'penalty': list(set(penalty for penalties in params.values() for penalty in penalties)),
    'C': [0.001, 0.01, 0.1, 1, 10, 100]
    
}

print(f"\033[1mparameters_dist\033[0m è: {parameters_dist}")

def generate_valid_params(params):
    valid_params = []
    
    # Generate values from 0 to 1 (inclusive) with step 0.05
    l1_ratio_values = np.append(np.arange(0.0, 1.0, 0.05), 1.0)

    # Impongo parametro C con valori su scala logaritmica 
    C_values = [0.001, 0.01, 0.1, 1, 10, 100]

    for C in C_values: 
        for solver in params['solver']:
            if solver == 'newton-cg':
                penalties = ['l2', None]
            elif solver == 'sag':
                penalties = ['l2', None]
            elif solver == 'lbfgs':
                penalties = ['l2', None]
            elif solver == 'saga':
                penalties = ['l1', 'l2', 'elasticnet', None]  # Include None here explicitly
            else:
                penalties = params['penalty']
            
            # Create parameter dictionaries for each combination of solver and penalty
            for penalty in penalties:
                if penalty == 'elasticnet':
                    for l1_ratio in l1_ratio_values:
                        valid_params.append({'solver': [solver], 'penalty': ['elasticnet'], 'l1_ratio': [l1_ratio], 'C': [C]})
                        
                else:
                    valid_params.append({'solver': [solver], 'penalty': [penalty], 'C': [C]})
    
    return valid_params


# Funzione per verificare se una combinazione di iperparametri è valida
def valid_param_combination(params):
    solver = params['solver']
    penalty = params['penalty']
    
    if solver in ['newton-cg', 'lbfgs', 'sag'] and penalty in ['l2', None]:
        return True
    elif solver == 'saga' and penalty in ['l1', 'l2', 'elasticnet', None]:
        return True
    else:
        return False

valid_params_list = generate_valid_params(parameters_dist)
print(f"\n\033[1mvalid_params_list\033[0m è: {valid_params_list}")



# Itera attraverso i soggetti

#for subject, subj_dict in subject_level_concatenations_th_1_20.items():
for subject, subj_dict in new_subject_level_concatenations_th_1_20.items():

    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO'''
    
    if subject == 'th_20':
    
    #if subject == 'th_17' or subject == 'th_18' or subject == 'th_19':
        
        print(f"\n\nCurrent Subject \033[1m{subject}\033[0m")

        print(f"\n\n\033[1mExtraction of Data\033[0m from Subject \033[1m{subject}\033[0m from Original Filtered Signal in \033[1m1-20Hz\033[0m")

        X = subj_dict['data'] # Estraiamo i dati del soggetto corrente

        y = subj_dict['labels'] # Estraiamo le labels livello corrente del soggetto corrente

        #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
        params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20'

        #FILE PATH DINAMICA PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
        #A SECONDA DEL SOGGETTO E LIVELLO DI RICOSTRUZIONE DEI DATI PRESI IN ESAME 

        # Costruzione del percorso del file in maniera dinamica
        params_file_path = f'{params_dir}/optimized_params_{subject}_filtered_1_20_std.txt'

        if not os.path.exists(params_dir):
            os.makedirs(params_dir)

        #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\t\033[1m{params_dir}\033[0m"),
        print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

        print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

        y = y.astype(int) 

        print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


        # Calcola il numero totale di etichette 
        label_counts = np.unique(y, return_counts = True)[1]
        total_labels = len(y)

        # Calcola la percentuale di ciascuna classe
        class_proportions = label_counts / total_labels * 100

        print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

        # Calcola i pesi delle classi come l'inverso delle proporzioni
        class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

        # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
        class_weights /= class_weights.sum()

        print(f"\n\033[1mClass Weights {class_weights}\033[0m")

        # Crea un dizionario per class_weight
        class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}

        '''INIZIALIZZAZIONE LOGISTIC REGRESSION'''

        # Inizializzo modello Logistic Regression base (da sklearn.LinearModel version 1.0.5)
        log_reg_base = LogisticRegression(class_weight = class_weight_dict, max_iter = 10000)

        # Memorizza il tempo di inizio
        start_time = time.time()

        # Lista per memorizzare i tempi di esecuzione per ogni istante temporale
        execution_times = []

        # Contatori per combinazioni valide e non valide
        valid_combination_count = 0
        invalid_combination_count = 0

        # File di output per i parametri ottimizzati
        with open(params_file_path, 'w') as f:
            f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")


        '''INIZIALIZZAZIONE RANDOM SEARCH'''

        # Inizializzazione della Random Search:

        #https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

        #cv: int, cross-validation generator or an iterable, default=None
        #Determines the cross-validation splitting strategy. 

        #Possible inputs for cv are:

        #None, to use the default 5-fold cross validation,
        #integer, to specify the number of folds in a (Stratified)KFold,
        #CV splitter,
        #An iterable yielding (train, test) splits as arrays of indices.

        #random_state: int, RandomState instance or None, default=None
        #Pseudo random number generator state used for random uniform sampling from lists of possible values 
        #instead of scipy.stats distributions. Pass an int for reproducible output across multiple function calls

        # RandomizedSearchCV è una tecnica di ricerca iperparametrica che 
        # campiona casualmente combinazioni di iperparametri da un insieme predefinito.

        #n_iter determina il numero di combinazioni di iperparametri da testare durante la ricerca


        # Lista per memorizzare i risultati delle finestre
        window_results = []

        # Creazione della finestra scorrevole con step e dimensioni desiderate
        n_samples = X.shape[2]
        window_size = 50
        step_size = 25
        n_windows = (n_samples - window_size) // step_size + 1


        ''' 
        50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 
        '''

        # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

        for window_start in range(0, n_samples - window_size + 1, step_size):

            # Memorizza il tempo di inizio per il punto temporale corrente
            time_point_start = time.time()

            # Definiamo la finestra corrente
            window_end = window_start + window_size

            X_window = X[:, :, window_start:window_end]
            print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

            # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
            X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
            print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

            # Standardizza i dati della finestra corrente
            scaler = StandardScaler()
            X_window_standardized = scaler.fit_transform(X_window_reshaped)
            print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

            #print(X_window_reshaped.shape)

            #Da https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

            #param_distributions: 

            #Dictionary with parameters names (str) as keys and distributions or lists of parameters to try. 
            #Distributions must provide a rvs method for sampling (such as those from scipy.stats.distributions). 
            #If a list is given, it is sampled uniformly. 
            #If a list of dicts is given, first a dict is sampled uniformly, 
            #and then a parameter is sampled using that dict as above.

            try:
                rand_search = RandomizedSearchCV(
                    estimator = log_reg_base,
                    param_distributions = valid_params_list,
                    scoring ='accuracy',
                    n_iter = 100,
                    verbose = 1,
                    n_jobs = -1
                )
                #random_state = 42 + window_start  # Corretto random_state

                '''
                50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 
                '''

                # Esegui RandomizedSearchCV sulla finestra corrente
                rand_search.fit(X_window_reshaped, y)

                # Controlla il numero totale di combinazioni testate
                total_combinations_tested = len(rand_search.cv_results_['params'])
                #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                # Controlla le combinazioni testate e conta quelle valide
                #valid_combinations_count = 0

                # Controlla le combinazioni testate
                #print(f"\n\033[1mValid hyperparameter combinations tested for n_window {window_start}-{window_end}\033[0m:\n")

                # Salva tutte le combinazioni testate per la finestra corrente
                with open(params_file_path, 'a') as f:
                    for i, params in enumerate(rand_search.cv_results_['params']):
                        score = rand_search.cv_results_['mean_test_score'][i]
                        f.write(f"Window {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n")

                    for params in rand_search.cv_results_['params']:
                        if valid_param_combination(params):
                            valid_combination_count += 1
                            #print(f"\033[1mSolver\033[0m: {params['solver']}, \033[1mPenalty\033[0m: {params['penalty']}, \033[1mC\033[0m: {params['C']}", end = '')
                            #if 'l1_ratio' in params:
                            #    print(f", \033[1ml1_ratio\033[0m: {params['l1_ratio']}")
                            #else:
                                #print()
                        else:
                            invalid_combination_count += 1
                            print(f"Invalid combination found: {params}")

                        #QUI

                    # Ottieni il modello con i migliori iper-parametri:

                    #Questa variabile ti restituisce il set di iper-parametri che ha prodotto il miglior punteggio 
                    #(migliore accuratezza) durante la Randomized Search per la finestra corrente. 
                    #È un dizionario che specifica valori come il solver, la penalizzazione, e altri iper-parametri.

                    best_model_params = rand_search.best_params_

                    '''
                    50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 
                    '''

                    #Questa variabile ti restituisce il punteggio (accuracy) del modello che ha ottenuto le migliori prestazioni 
                    #con i parametri in rand_search.best_params_. 
                    #Rappresenta la misura delle performance del modello sui dati di validazione durante la Randomized Search.

                    best_score = rand_search.best_score_

                    '''
                    50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 
                    '''
                    # Memorizza i risultati della finestra corrente
                    window_results.append({
                        'window_start': window_start,
                        'window_end': window_end,
                        'best_params': best_model_params,
                        'best_score': best_score
                    })

                    '''
                    50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 
                    '''
                    # Stampa i risultati per la finestra corrente
                    #print(f"\033[1mWindow {window_start}-{window_end}\033[0m: Best Params = {best_model_params}, Best Score = {best_score}")

                # Salva i parametri migliori per la finestra temporale corrente in una riga del file di testo
                #with open(params_file_path, 'a') as f:
                #    f.write(f"Window n° {time_point}\t{json.dumps(best_model_params)}\n")

                    # Salva i parametri migliori per la finestra corrente in una riga del file di testo
                with open(params_file_path, 'a') as f:
                    f.write('\n')
                    f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                    f.write('\n')

            except Exception as e:
                print(f"An error occurred for window {window_start}-{window_end}: {e}")
                invalid_combination_count += 1

                # Continua con l'iterazione successiva senza interrompere l'intero loop

            # Memorizza il tempo di fine per il punto temporale corrente
            time_point_end = time.time()

            # Calcola il tempo di esecuzione per il punto temporale corrente
            time_point_elapsed = time_point_end - time_point_start

            # Aggiungi il tempo di esecuzione alla lista
            execution_times.append(time_point_elapsed)

            # Stampa i risultati per il punto temporale corrente
            #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
            #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
            #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
            #print()
            #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds")
            #print()


        # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

        # Definisci il range generale delle finestre che vuoi analizzare
        general_range = [0, 300]  # Puoi modificare il range se necessario

        # Filtra i risultati delle finestre nel range desiderato
        general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

        # Controlla se ci sono risultati validi all'interno del range specificato
        if general_results:

            # Trova la finestra con il punteggio migliore
            best_general_window = max(general_results, key=lambda x: x['best_score'])

            # Trova i parametri migliori per questa finestra specifica (se disponibili)
            best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
            best_general_window['best_params'] = best_params

            # Stampa le informazioni sulla finestra migliore trovata
            #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
            #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
            #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

        else:
            print("No valid windows found in the specified range.")


        # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
        window_results.append({
            'Best window_start': best_general_window['window_start'] if general_results else None,
            'Best window_end': best_general_window['window_end'] if general_results else None,
            'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
            'best_score': best_general_window['best_score'] if general_results else None
        })

        # Calcola il tempo di esecuzione totale
        end_time = time.time()
        total_execution_time = end_time - start_time

        #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
        #print()
        #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
        #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

        # Aggiungi il risultato della migliore finestra generale al file di testo
        with open(params_file_path, 'a') as f:
            f.write('\n')
            if general_results:
                best_general_window = max(general_results, key=lambda x: x['best_score'])
                f.write(f"BEST WINDOW OVERALL: "),
                f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                f.write(f"\nBest Score: {best_general_window['best_score']}")

                if best_general_window['best_params'] is not None:
                    f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
            else:
                f.write("No valid windows found in the specified range.\n")

            f.write('\n')
            f.write(f"Total execution time: {total_execution_time} seconds\n")
            f.write(f"Number of valid combinations: {valid_combination_count}\n")
            f.write(f"Number of invalid combinations: {invalid_combination_count}\n")


#### **ALL SINGLE Therapists (TH01-TH20) for **COUPLED EXPERIMENTAL CONDITIONS****

#### Automatization of all steps from: 

1) "**new_subject_level_concatenations_coupled_exp_th**" ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_coupled_exp_th_1_20**": EEG preprocessed signal filtered 1-20Hz 

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''


#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
#    new_subject_level_concatenations_th = pickle.load(f)
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle
import numpy as np


with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th_1_20 = pickle.load(f)
    


    
    
#PER SALVARE I FILE
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('NOME DEL FILE.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations, f)


#subject_level_concatenations_th['th_1'].keys()

In [ ]:
print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_th\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()}")

In [ ]:
np.unique(new_subject_level_concatenations_coupled_exp_th['th_20']['theta']['baseline_vs_th_resp']['labels'],return_counts=True)

##### **Descrizione degli step nel codice per ottenere e salvare nelle paths le best score performances per il level 4 e 5 dalle ricostruzioni**:

Vorrei in questo caso, per velocizzare, iterare su 

subject_level_concatenations, che ha questa struttura...

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


al cui interno ha per ogni chiave di primo ordine, un altro dizionario annidato, che è fatto di queste chiavi


dict_keys(['theta', 'delta', 'labels'])

dentro 'theta' e 'delta' ci sono tutti i dati di tutte le condizioni sperimentali del singolo soggetto

del tipo 'theta' o 'delta' conterrà un array con shape

(204, 3, 300)

con 1° dimensione i trial, poi i canali, poi i punti di ogni trial (campioni EEG)

e dentro 'labels' ho invece l'array delle labels concatenate...
(204,)


<br>


Ora però, vorrei che ... 

Se ad esempio nel soggetto 'th_1' entri nella chiave 'theta', 

allora poi il file corrispondente .txt deve essere scritto con una path dinamica, che cambia a seconda 
- sia del soggetto iterato
- sia del livello di ricostruzione dei dati

Ossia:

la "params_dir" è fissa

mentre 

"params_file_path" è dinamica, e cambia a seconda del soggetto iterato e del livello. 

Per cui sarà una composizione di stringhe fisse e stringhe 'mobili', ossia

'params_file_path' = 'optimized_params_' + {subject} dove subject dovrebbe essere una lista di stringhe che si preleva dalle chiavi di primo ordine di "subject_level_concatenations" che erano

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


seguito da "_level_{level}_std" dove {level} dipende dal nome della chiave del sotto-dizionario iterato per ogni soggetto...

Ossia, ad esempio dentro il sotto-dizionario del primo soggetto di "subject_level_concatenations" cioè

subject_level_concatenations['th_1'], 

Se la sua sotto-chiave è 'theta' allora il level = 4, se la chiave è 'delta' allora il level = 5, 



Quindi la costruzione finale della path dinamica del file specifico per il soggetto 1 deve essere

 
params_file_path = 'optimized_params_' +'{subject}' + "_level_{level}_std.txt"

e sarà se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_1' + "_level_4_std.txt"


e sarà se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_1' + "_level_5_std.txt"


in questo modo, farei un loop unico su tutte le sottochiavi dei dizionari annidati dentro 
"subject_level_concatenations" 

ossia 
dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

e per ognuno vedo se la sua sotto-chiave sarà 'theta' o 'delta' e creerà dei file .txt corrispondenti nella param_dir che gli ho chiesto...

Il resto del codice non toccarlo invece, perché dovrebbe creare dei file .txt per ogni soggetto per ogni livello di ricostruzione dei dati,
e salverà le analisi nel file .txt corrispondente



Ad esempio, continuando col soggetto 2:

la costruzione finale della path dinamica del file specifico per il soggetto 2

Sarà, se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_2' + "_level_4_std.txt"


e sarà, se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_2' + "_level_5_std.txt"


e così via per tutti gli altri soggetti




##### **ALL SINGLE Therapists (TH01-TH16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DALLE RICOSTRUZIONI** 

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**


###### **ISTRUZIONI PER MODIFICHE AL CASO 2 CLASSI**

Allora, andiamo per step:

**1)** la nuova variabile sulla quale iterare è new_subject_level_concatenations_coupled_exp_th

che è fatta con questa struttura

print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_th\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()}")

OUTPUT:

Dataset Organization: new_subject_level_concatenations_coupled_exp_th

First Order Key: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16'])

Second Order Key: dict_keys(['theta', 'delta', 'theta_strict'])

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

Fourth Order Key: dict_keys(['data', 'labels'])

quindi significa che, per ogni soggetto, tu dovrai entrare nella sotto sotto chiave relativa ai livelli di ricostruzione del segnale 

dict_keys(['theta', 'delta', 'theta_strict'])

per ognuna di queste, avrai appunto delle altre sotto-sotto-sotto chiavi, che sono le condizioni sperimentali, sulle quali dovrai entrare che sono 

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

dopodiché dentro ognuna di queste, dovrai entrare ulteriormente dentro ciascuna sotto chiave di quarto livello:

la prima, che fa riferimento ai dati('data') il cui valore (array numpy() verrà assegnato ad X nel codice, e 
la seconda, la chiave delle labels ('labels') il cui valore verrà assegnato ad Y...

**2)** questa parte relativa ai print

 for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'

voglio che poi abbia degli altri if, nel senso che vorrei che iterando su ogni livello, voglio che venga applicata la stessa logica dei printing di qui sopra, ma alle chiavi del 3° livello, ossia quelle che fanno riferimento alle condizioni sperimentali...

ossia, 

voglio che ci sia scritto per le X

print(f"\n\033[1mExtraction of Data\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

e voglio che ci sia scritto per le Y

print(f"\n\033[1mExtraction of Labels\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

dove 

"experimental_condition" farà riferimento alla chiave della condizione sperimentale iterata in quel loop, e 

"level_key" invece farà riferimento alle chiavi del 2° livello, ossia a quelle che si riferiscono allo specifico livello di ricostruzione del segnale per il quale io sto estraendo i dati e le labels al ciclo corrente...

In questo modo, dovrei avere un'idea dai print del mio codice, quando viene eseguito, su quale soggetto, quale livello e quale condizione sperimentale sta eseguendo i calcoli.. 

**3)** voglio che vengano create dei folder nuovi per appendere i risultati di tutte le elaborazioni da parte dei vari modelli e che saranno queste due cartelle

"EEG_50_window_25_overlap_coupled_exp_cond" 
"single_therapist_optimized_params_coupled_exp_cond"
 
ossia la mia directory dovrebbe diventare

params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond'

per cui, se "EEG_50_window_25_overlap_coupled_exp_cond" né "single_therapist_optimized_params_coupled_exp_cond" non sono state create, allora andranno create...

**4)** la creazione del nome del file relativo ad un determinato soggetto dovrà essere formato in questo modo

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

dove, ricorda, "experimental_condition" farà riferimento alle insieme delle stringhe che compongono la chiave della condizione sperimentale iterata in quel loop (chiavi di 3° livello di "new_subject_level_concatenations_coupled_exp_th" 

del tipo potrebbe essere

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

Con ad esempio:

subject = th_1
level = theta 
experimental_condition = baseline_vs_th_resp

per cui sarebbe 

f'{params_dir}/optimized_params_th_1_level_theta_baseline_vs_th_resp_std.txt'

**5)** al momento, il settaggio degli iper-parametri è impostato per anche per i casi multi-nomiali ma in questo caso il codice verrà usato per task di classificazione binaria...

per cui, voglio essere sicuro che l'impostazione attuale vada anche bene per i casi semplicemente binomiali, ossia di due possibili classi solo...

per farlo, ti do il link della pagina della Logistic Regression, in modo che tu mi dica se l'attuale implementazione sia corretta....

https://scikit-learn.org/1.5/modules/generated/sklearn.linear_model.LogisticRegression.html


**6)** Fai le modifiche a quello che ti ho chiesto, non azzardare cose in più od in meno, vorrei che ti attenessi a ciò che ti ho chiesto...


##### **IMPLEMENTATION LOGISTIC REGRESSION FOR COUPLED EXPERIMENTAL CONDITIONS**

In [ ]:
new_subject_level_concatenations_coupled_exp_th['th_20']['theta']['baseline_vs_th_resp'].keys()

In [ ]:
''' THERAPISTS!

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ, Θ, δ e Θ strict!)


******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* *******
#DIRECTORY PATH MESSA INIZIALMENTE  

# -->>>>> /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/prova/ <<<<<--

#PER NON SOVRASCRIVERE RISULTATI RANDOM SEARCH SU TUTTI I SOGGETTI CON LOGISTIC REGRESSION!!!!!

******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* *******


Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare

#Some penalties may not work with some solvers. 
#See the parameter solver below, to know the compatibility between the penalty and solver.


Per la classificazione multi-classe con l'opzione multi_class='multinomial', 
puoi utilizzare i seguenti solver e le relative penalità:

newton-cg: supporta solo l2 e None.
sag: supporta solo l2 e None.
saga: supporta l1, l2, elasticnet, e None.
lbfgs: supporta solo l2 e None.

Quindi, se vuoi esplorare solo il caso multinomiale, puoi utilizzare i seguenti abbinamenti di solver e penalità:

newton-cg: l2, None
sag: l2, None
saga: l1, l2, elasticnet, None
lbfgs: l2, None

'''

import numpy as np
import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

import torch

'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER MULTINOMIAL LOGISTIC REGRESSION'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra penalty e solver, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...


# Definizione dei parametri validi, ossia delle coppie solver-penalty associate
params = {'newton-cg': ['l2', None],
    'sag': ['l2', None],
    'saga': ['l1', 'l2', 'elasticnet', None],
    'lbfgs': ['l2', None]
}


# Assicuriamoci di non avere duplicati e di avere una lista di dizionari separati per solver e penalty
parameters_dist = {
    'solver': list(params.keys()),
    'penalty': list(set(penalty for penalties in params.values() for penalty in penalties)),
    'C': [0.001, 0.01, 0.1, 1, 10, 100]
    
}

print(f"\033[1mparameters_dist\033[0m è: {parameters_dist}")

def generate_valid_params(params):
    valid_params = []
    
    # Generate values from 0 to 1 (inclusive) with step 0.05
    l1_ratio_values = np.append(np.arange(0.0, 1.0, 0.05), 1.0)

    # Impongo parametro C con valori su scala logaritmica 
    C_values = [0.001, 0.01, 0.1, 1, 10, 100]

    for C in C_values: 
        for solver in params['solver']:
            if solver == 'newton-cg':
                penalties = ['l2', None]
            elif solver == 'sag':
                penalties = ['l2', None]
            elif solver == 'lbfgs':
                penalties = ['l2', None]
            elif solver == 'saga':
                penalties = ['l1', 'l2', 'elasticnet', None]  # Include None here explicitly
            else:
                penalties = params['penalty']
            
            # Create parameter dictionaries for each combination of solver and penalty
            for penalty in penalties:
                if penalty == 'elasticnet':
                    for l1_ratio in l1_ratio_values:
                        valid_params.append({'solver': [solver], 'penalty': ['elasticnet'], 'l1_ratio': [l1_ratio], 'C': [C]})
                        
                else:
                    valid_params.append({'solver': [solver], 'penalty': [penalty], 'C': [C]})
    
    return valid_params


# Funzione per verificare se una combinazione di iperparametri è valida
def valid_param_combination(params):
    solver = params['solver']
    penalty = params['penalty']
    
    if solver in ['newton-cg', 'lbfgs', 'sag'] and penalty in ['l2', None]:
        return True
    elif solver == 'saga' and penalty in ['l1', 'l2', 'elasticnet', None]:
        return True
    else:
        return False

valid_params_list = generate_valid_params(parameters_dist)
print(f"\n\033[1mvalid_params_list\033[0m è: {valid_params_list}")




# Itera attraverso i soggetti

'''OLD VERSION'''
#for subject, levels in subject_level_concatenations.items():

'''NEW VERSION'''
#for subject, levels in new_subject_level_concatenations_th.items():


'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond"

# Iterazione sulla struttura `new_subject_level_concatenations_coupled_exp_th`

for subject, levels in new_subject_level_concatenations_coupled_exp_th.items():
    
    #if subject == 'th_6'or subject == 'th_6'or  
    
    #if subject == 'th_17' or subject == 'th_18' or subject == 'th_19':
    #if subject == 'th_20':
        
    print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")

    for level_key, experimental_condition in levels.items():

        # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
        #                                      'delta' = δ,i.e., approx_5 ,
        #                                      'theta_strict' = Θ, i.e., detail_5,
        #                                      'labels') 

        # Identificazione del livello
        if level_key == 'theta':
            level = "approx_4"


        elif level_key == 'delta':
            level = "approx_5"


        elif level_key == 'theta_strict':
            level = "detail_5"

        else:
            continue  # Ignora livelli non rilevanti


        print(f"\nProcessing Data \033[1m from Level: \033[1m{level_key}\033[0m for Subject \033[1m{subject}\033[0m")

        for condition, data_dict in experimental_condition.items():

            # Estrazione dei dati e delle label
            X = data_dict['data'] # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente

            # Messaggi di log per dati e label
            print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

            print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

            y = data_dict['labels'] # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente


            '''NEW VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            params_dir = params_dir

            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f"{params_dir}/optimized_params_{subject}_level_{level}_{condition}_std.txt"

            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")
            print(f"033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE LOGISTIC REGRESSION

            # Inizializzo modello Logistic Regression base (da sklearn.LinearModel version 1.0.5)
            log_reg_base = LogisticRegression(class_weight = class_weight_dict, max_iter = 20000)

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni istante temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0


            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")


                '''INIZIALIZZAZIONE RANDOM SEARCH'''

                # Inizializzazione della Random Search:

                #https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

                #cv: int, cross-validation generator or an iterable, default=None
                #Determines the cross-validation splitting strategy. 

                #Possible inputs for cv are:

                #None, to use the default 5-fold cross validation,
                #integer, to specify the number of folds in a (Stratified)KFold,
                #CV splitter,
                #An iterable yielding (train, test) splits as arrays of indices.

                #random_state: int, RandomState instance or None, default=None
                #Pseudo random number generator state used for random uniform sampling from lists of possible values 
                #instead of scipy.stats distributions. Pass an int for reproducible output across multiple function calls

                # RandomizedSearchCV è una tecnica di ricerca iperparametrica che 
                # campiona casualmente combinazioni di iperparametri da un insieme predefinito.

                #n_iter determina il numero di combinazioni di iperparametri da testare durante la ricerca


                # Lista per memorizzare i risultati delle finestre
                window_results = []

                # Creazione della finestra scorrevole con step e dimensioni desiderate
                n_samples = X.shape[2]
                window_size = 50
                step_size = 25
                n_windows = (n_samples - window_size) // step_size + 1


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente
                for window_start in range(0, n_samples - window_size + 1, step_size):

                    # Memorizza il tempo di inizio per il punto temporale corrente
                    time_point_start = time.time()

                    # Definiamo la finestra corrente
                    window_end = window_start + window_size

                    X_window = X[:, :, window_start:window_end]
                    print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                    # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                    X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                    print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                    # Standardizza i dati della finestra corrente
                    scaler = StandardScaler()
                    X_window_standardized = scaler.fit_transform(X_window_reshaped)
                    print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                    #print(X_window_reshaped.shape)

                    #Da https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

                    #param_distributions: 

                    #Dictionary with parameters names (str) as keys and distributions or lists of parameters to try. 
                    #Distributions must provide a rvs method for sampling (such as those from scipy.stats.distributions). 
                    #If a list is given, it is sampled uniformly. 
                    #If a list of dicts is given, first a dict is sampled uniformly, 
                    #and then a parameter is sampled using that dict as above.

                    try:
                        rand_search = RandomizedSearchCV(
                            estimator = log_reg_base,
                            param_distributions = valid_params_list,
                            scoring ='accuracy',
                            n_iter = 100,
                            verbose = 1,
                            n_jobs = -1
                        )
                        #random_state = 42 + window_start  # Corretto random_state


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Esegui RandomizedSearchCV sulla finestra corrente
                        rand_search.fit(X_window_reshaped, y)

                        # Controlla il numero totale di combinazioni testate
                        total_combinations_tested = len(rand_search.cv_results_['params'])
                        #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                        # Controlla le combinazioni testate e conta quelle valide
                        #valid_combinations_count = 0

                        # Controlla le combinazioni testate
                        #print(f"\n\033[1mValid hyperparameter combinations tested for n_window {window_start}-{window_end}\033[0m:\n")

                        # Salva tutte le combinazioni testate per la finestra corrente
                        with open(params_file_path, 'a') as f:
                            for i, params in enumerate(rand_search.cv_results_['params']):
                                score = rand_search.cv_results_['mean_test_score'][i]
                                f.write(f"Window {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n")

                            for params in rand_search.cv_results_['params']:
                                if valid_param_combination(params):
                                    valid_combination_count += 1
                                    #print(f"\033[1mSolver\033[0m: {params['solver']}, \033[1mPenalty\033[0m: {params['penalty']}, \033[1mC\033[0m: {params['C']}", end = '')
                                    #if 'l1_ratio' in params:
                                    #    print(f", \033[1ml1_ratio\033[0m: {params['l1_ratio']}")
                                    #else:
                                    #    print()
                                else:
                                    invalid_combination_count += 1
                                    #print(f"Invalid combination found: {params}")

                                #QUI

                            # Ottieni il modello con i migliori iper-parametri:

                            #Questa variabile ti restituisce il set di iper-parametri che ha prodotto il miglior punteggio 
                            #(migliore accuratezza) durante la Randomized Search per la finestra corrente. 
                            #È un dizionario che specifica valori come il solver, la penalizzazione, e altri iper-parametri.

                            best_model_params = rand_search.best_params_


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                            #Questa variabile ti restituisce il punteggio (accuracy) del modello che ha ottenuto le migliori prestazioni 
                            #con i parametri in rand_search.best_params_. 
                            #Rappresenta la misura delle performance del modello sui dati di validazione durante la Randomized Search.

                            best_score = rand_search.best_score_


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                            # Memorizza i risultati della finestra corrente
                            window_results.append({
                                'window_start': window_start,
                                'window_end': window_end,
                                'best_params': best_model_params,
                                'best_score': best_score
                            })


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                            # Stampa i risultati per la finestra corrente
                            #print(f"\033[1mWindow {window_start}-{window_end}\033[0m: Best Params = {best_model_params}, Best Score = {best_score}")

                        # Salva i parametri migliori per la finestra temporale corrente in una riga del file di testo
                        #with open(params_file_path, 'a') as f:
                        #    f.write(f"Window n° {time_point}\t{json.dumps(best_model_params)}\n")

                            # Salva i parametri migliori per la finestra corrente in una riga del file di testo
                        with open(params_file_path, 'a') as f:
                            f.write('\n')
                            f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                            f.write('\n')

                    except Exception as e:
                        print(f"An error occurred for window {window_start}-{window_end}: {e}")
                        invalid_combination_count += 1

                        # Continua con l'iterazione successiva senza interrompere l'intero loop

                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds")
                    #print()


                # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

                # Definisci il range generale delle finestre che vuoi analizzare
                general_range = [0, 300]  # Puoi modificare il range se necessario

                # Filtra i risultati delle finestre nel range desiderato
                general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

                # Controlla se ci sono risultati validi all'interno del range specificato
                if general_results:

                    # Trova la finestra con il punteggio migliore
                    best_general_window = max(general_results, key=lambda x: x['best_score'])

                    # Trova i parametri migliori per questa finestra specifica (se disponibili)
                    best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                    best_general_window['best_params'] = best_params

                    # Stampa le informazioni sulla finestra migliore trovata
                    #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                    #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                    #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

                else:
                    print("No valid windows found in the specified range.")


                # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
                window_results.append({
                    'Best window_start': best_general_window['window_start'] if general_results else None,
                    'Best window_end': best_general_window['window_end'] if general_results else None,
                    'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                    'best_score': best_general_window['best_score'] if general_results else None
                })

                # Calcola il tempo di esecuzione totale
                end_time = time.time()
                total_execution_time = end_time - start_time

                #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
                #print()
                #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
                #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

                # Aggiungi il risultato della migliore finestra generale al file di testo
                with open(params_file_path, 'a') as f:
                    f.write('\n')
                    if general_results:
                        best_general_window = max(general_results, key=lambda x: x['best_score'])
                        f.write(f"BEST WINDOW OVERALL: "),
                        f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                        f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                        f.write(f"\nBest Score: {best_general_window['best_score']}")

                        if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n")

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **EEG preprocessed signal**: filtered 1-20

In [ ]:
#new_subject_level_concatenations_th_1_20.keys()
#new_subject_level_concatenations_th_1_20['th_1'].keys()

#new_subject_level_concatenations_coupled_exp_th.keys()

#new_subject_level_concatenations_coupled_exp_th_1_20.keys()
#new_subject_level_concatenations_coupled_exp_th_1_20['th_1'].keys()


#new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp'].keys()

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import pickle
import numpy as np


with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th_1_20 = pickle.load(f)

In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun livello temporale (th_1, th_2, ..., th_16)
for id_subj in new_subject_level_concatenations_coupled_exp_th_1_20.keys():
    
    # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
    for exp_cond in new_subject_level_concatenations_coupled_exp_th_1_20[id_subj].keys():
        
        # Verifica che 'data' sia presente tra le chiavi della condizione
        if 'data' in new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]:
            
            # Estrai i dati originali
            dati_originali = new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]['data']
            
            # Sotto-seleziona i canali di interesse
            dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali
            
            # Aggiorna la chiave 'data' con i dati filtrati
            new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]['data'] = dati_sottoselezionati

            # Opzionale: stampa di controllo per verificare la nuova forma dei dati
            print(f"Subj \033[1m{id_subj}\033[0m, Condizione \033[1m{exp_cond}\033[0m: {dati_sottoselezionati.shape}")

In [ ]:
new_subject_level_concatenations_coupled_exp_th_1_20.keys()
np.unique(new_subject_level_concatenations_coupled_exp_th_1_20['th_5']['th_resp_vs_pt_resp']['labels'], return_counts = True)

In [ ]:
new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp'].keys()


In [ ]:
##### **ALL SINGLE Therapists (TH01-TH16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DAL SEGNALE 1-20Hz**

import numpy as np
import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER MULTINOMIAL LOGISTIC REGRESSION'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra penalty e solver, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...


# Definizione dei parametri validi, ossia delle coppie solver-penalty associate
params = {'newton-cg': ['l2', None],
    'sag': ['l2', None],
    'saga': ['l1', 'l2', 'elasticnet', None],
    'lbfgs': ['l2', None]
}


# Assicuriamoci di non avere duplicati e di avere una lista di dizionari separati per solver e penalty
parameters_dist = {
    'solver': list(params.keys()),
    'penalty': list(set(penalty for penalties in params.values() for penalty in penalties)),
    'C': [0.001, 0.01, 0.1, 1, 10, 100]
    
}

print(f"\033[1mparameters_dist\033[0m è: {parameters_dist}")

def generate_valid_params(params):
    valid_params = []
    
    # Generate values from 0 to 1 (inclusive) with step 0.05
    l1_ratio_values = np.append(np.arange(0.0, 1.0, 0.05), 1.0)

    # Impongo parametro C con valori su scala logaritmica 
    C_values = [0.001, 0.01, 0.1, 1, 10, 100]

    for C in C_values: 
        for solver in params['solver']:
            if solver == 'newton-cg':
                penalties = ['l2', None]
            elif solver == 'sag':
                penalties = ['l2', None]
            elif solver == 'lbfgs':
                penalties = ['l2', None]
            elif solver == 'saga':
                penalties = ['l1', 'l2', 'elasticnet', None]  # Include None here explicitly
            else:
                penalties = params['penalty']
            
            # Create parameter dictionaries for each combination of solver and penalty
            for penalty in penalties:
                if penalty == 'elasticnet':
                    for l1_ratio in l1_ratio_values:
                        valid_params.append({'solver': [solver], 'penalty': ['elasticnet'], 'l1_ratio': [l1_ratio], 'C': [C]})
                        
                else:
                    valid_params.append({'solver': [solver], 'penalty': [penalty], 'C': [C]})
    
    return valid_params


# Funzione per verificare se una combinazione di iperparametri è valida
def valid_param_combination(params):
    solver = params['solver']
    penalty = params['penalty']
    
    if solver in ['newton-cg', 'lbfgs', 'sag'] and penalty in ['l2', None]:
        return True
    elif solver == 'saga' and penalty in ['l1', 'l2', 'elasticnet', None]:
        return True
    else:
        return False

valid_params_list = generate_valid_params(parameters_dist)
print(f"\n\033[1mvalid_params_list\033[0m è: {valid_params_list}")


'''
# Itera su ciascun livello temporale (th_1, th_2, ..., th_16)
for id_subj in new_subject_level_concatenations_coupled_exp_th_1_20.keys():
    
    # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
    for exp_cond in new_subject_level_concatenations_coupled_exp_th_1_20[id_subj].keys():
        
        # Verifica che 'data' sia presente tra le chiavi della condizione
        if 'data' in new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]:
            
            # Estrai i dati originali
            dati_originali = new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]['data']
            
            # Sotto-seleziona i canali di interesse
            dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali
            
            # Aggiorna la chiave 'data' con i dati filtrati
            new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]['data'] = dati_sottoselezionati

            # Opzionale: stampa di controllo per verificare la nuova forma dei dati
            print(f"Subj \033[1m{id_subj}\033[0m, Condizione \033[1m{exp_cond}\033[0m: {dati_sottoselezionati.shape}")
'''
'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond_1_20"

for idx_subj, subject_data in new_subject_level_concatenations_coupled_exp_th_1_20.items():
    
    level_str = 'filtered_1_20'
    
    #if id_subj == 'th_1':
    #if idx_subj == 'th_17' or idx_subj == 'th_18' or idx_subj == 'th_19':
    
    #if idx_subj == 'th_5' or idx_subj == 'th_20':
        
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {idx_subj}\033[0m\n\n")

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        #for condition in new_subject_level_concatenations_coupled_exp_th_1_20[idx_subj].keys():

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        for condition, condition_data in subject_data.items():

            #print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Creazione stringa per salvataggio files ('filtered_1_20')
            #level_str == 'filtered_1_20'

            print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente
            #X = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['data']

            # Estrazione dei dati e delle etichette
            X = condition_data['data']


            # Messaggi di log per dati e label
            print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente
            #y = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['labels'] 

            y = condition_data['labels']

            print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            '''NEW VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            params_dir = params_dir

            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f"{params_dir}/optimized_params_{idx_subj}_level_{level_str}_{condition}_std.txt"

            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{idx_subj}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")

            print(f"\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE LOGISTIC REGRESSION

            # Inizializzo modello Logistic Regression base (da sklearn.LinearModel version 1.0.5)
            log_reg_base = LogisticRegression(class_weight = class_weight_dict, max_iter = 20000)

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni istante temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0


            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")


                '''INIZIALIZZAZIONE RANDOM SEARCH'''

                # Inizializzazione della Random Search:

                #https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

                #cv: int, cross-validation generator or an iterable, default=None
                #Determines the cross-validation splitting strategy. 

                #Possible inputs for cv are:

                #None, to use the default 5-fold cross validation,
                #integer, to specify the number of folds in a (Stratified)KFold,
                #CV splitter,
                #An iterable yielding (train, test) splits as arrays of indices.

                #random_state: int, RandomState instance or None, default=None
                #Pseudo random number generator state used for random uniform sampling from lists of possible values 
                #instead of scipy.stats distributions. Pass an int for reproducible output across multiple function calls

                # RandomizedSearchCV è una tecnica di ricerca iperparametrica che 
                # campiona casualmente combinazioni di iperparametri da un insieme predefinito.

                #n_iter determina il numero di combinazioni di iperparametri da testare durante la ricerca


                # Lista per memorizzare i risultati delle finestre
                window_results = []

                # Creazione della finestra scorrevole con step e dimensioni desiderate
                n_samples = X.shape[2]
                window_size = 50
                step_size = 25
                n_windows = (n_samples - window_size) // step_size + 1


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente
                for window_start in range(0, n_samples - window_size + 1, step_size):

                    # Memorizza il tempo di inizio per il punto temporale corrente
                    time_point_start = time.time()

                    # Definiamo la finestra corrente
                    window_end = window_start + window_size

                    X_window = X[:, :, window_start:window_end]
                    print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                    # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                    X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                    print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                    # Standardizza i dati della finestra corrente
                    scaler = StandardScaler()
                    X_window_standardized = scaler.fit_transform(X_window_reshaped)
                    print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                    #print(X_window_reshaped.shape)

                    #Da https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

                    #param_distributions: 

                    #Dictionary with parameters names (str) as keys and distributions or lists of parameters to try. 
                    #Distributions must provide a rvs method for sampling (such as those from scipy.stats.distributions). 
                    #If a list is given, it is sampled uniformly. 
                    #If a list of dicts is given, first a dict is sampled uniformly, 
                    #and then a parameter is sampled using that dict as above.

                    try:
                        rand_search = RandomizedSearchCV(
                            estimator = log_reg_base,
                            param_distributions = valid_params_list,
                            scoring ='accuracy',
                            n_iter = 100,
                            verbose = 1,
                            n_jobs = -1
                        )
                        #random_state = 42 + window_start  # Corretto random_state


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Esegui RandomizedSearchCV sulla finestra corrente
                        rand_search.fit(X_window_reshaped, y)

                        # Controlla il numero totale di combinazioni testate
                        total_combinations_tested = len(rand_search.cv_results_['params'])
                        #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                        # Controlla le combinazioni testate e conta quelle valide
                        #valid_combinations_count = 0

                        # Controlla le combinazioni testate
                        #print(f"\n\033[1mValid hyperparameter combinations tested for n_window {window_start}-{window_end}\033[0m:\n")

                        # Salva tutte le combinazioni testate per la finestra corrente
                        with open(params_file_path, 'a') as f:
                            for i, params in enumerate(rand_search.cv_results_['params']):
                                score = rand_search.cv_results_['mean_test_score'][i]
                                f.write(f"Window {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n")

                            for params in rand_search.cv_results_['params']:
                                if valid_param_combination(params):
                                    valid_combination_count += 1
                                    #print(f"\033[1mSolver\033[0m: {params['solver']}, \033[1mPenalty\033[0m: {params['penalty']}, \033[1mC\033[0m: {params['C']}", end = '')
                                    #if 'l1_ratio' in params:
                                    #    print(f", \033[1ml1_ratio\033[0m: {params['l1_ratio']}")
                                    #else:
                                    #    print()
                                else:
                                    invalid_combination_count += 1
                                    #print(f"Invalid combination found: {params}")

                                #QUI

                            # Ottieni il modello con i migliori iper-parametri:

                            #Questa variabile ti restituisce il set di iper-parametri che ha prodotto il miglior punteggio 
                            #(migliore accuratezza) durante la Randomized Search per la finestra corrente. 
                            #È un dizionario che specifica valori come il solver, la penalizzazione, e altri iper-parametri.

                            best_model_params = rand_search.best_params_


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                            #Questa variabile ti restituisce il punteggio (accuracy) del modello che ha ottenuto le migliori prestazioni 
                            #con i parametri in rand_search.best_params_. 
                            #Rappresenta la misura delle performance del modello sui dati di validazione durante la Randomized Search.

                            best_score = rand_search.best_score_


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                            # Memorizza i risultati della finestra corrente
                            window_results.append({
                                'window_start': window_start,
                                'window_end': window_end,
                                'best_params': best_model_params,
                                'best_score': best_score
                            })


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                            # Stampa i risultati per la finestra corrente
                            #print(f"\033[1mWindow {window_start}-{window_end}\033[0m: Best Params = {best_model_params}, Best Score = {best_score}")

                        # Salva i parametri migliori per la finestra temporale corrente in una riga del file di testo
                        #with open(params_file_path, 'a') as f:
                        #    f.write(f"Window n° {time_point}\t{json.dumps(best_model_params)}\n")

                            # Salva i parametri migliori per la finestra corrente in una riga del file di testo
                        with open(params_file_path, 'a') as f:
                            f.write('\n')
                            f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                            f.write('\n')

                    except Exception as e:
                        print(f"An error occurred for window {window_start}-{window_end}: {e}")
                        invalid_combination_count += 1

                        # Continua con l'iterazione successiva senza interrompere l'intero loop

                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds")
                    #print()


                # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

                # Definisci il range generale delle finestre che vuoi analizzare
                general_range = [0, 300]  # Puoi modificare il range se necessario

                # Filtra i risultati delle finestre nel range desiderato
                general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

                # Controlla se ci sono risultati validi all'interno del range specificato
                if general_results:

                    # Trova la finestra con il punteggio migliore
                    best_general_window = max(general_results, key=lambda x: x['best_score'])

                    # Trova i parametri migliori per questa finestra specifica (se disponibili)
                    best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                    best_general_window['best_params'] = best_params

                    # Stampa le informazioni sulla finestra migliore trovata
                    #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                    #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                    #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

                else:
                    print("No valid windows found in the specified range.")


                # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
                window_results.append({
                    'Best window_start': best_general_window['window_start'] if general_results else None,
                    'Best window_end': best_general_window['window_end'] if general_results else None,
                    'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                    'best_score': best_general_window['best_score'] if general_results else None
                })

                # Calcola il tempo di esecuzione totale
                end_time = time.time()
                total_execution_time = end_time - start_time

                #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
                #print()
                #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
                #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

                # Aggiungi il risultato della migliore finestra generale al file di testo
                with open(params_file_path, 'a') as f:
                    f.write('\n')
                    if general_results:
                        best_general_window = max(general_results, key=lambda x: x['best_score'])
                        f.write(f"BEST WINDOW OVERALL: "),
                        f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                        f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                        f.write(f"\nBest Score: {best_general_window['best_score']}")

                        if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n")


#### **ALL SINGLE Therapists (TH01-TH20)**

#### **PLOTS of EACH SINGLE Subject's Accuracy Score Performances** 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, θ and δ)**

<br>

#### Apri cella qui sotto per **istruzione da fornire per il codice**

##### **Descrizione degli step nel codice per estrarre dalle paths le best score performances salvate per il level 4 e 5 dalle ricostruzioni**:

Fammi un codice python che faccia queste cose 

- **1)** Entrami in una **folder path** (che ti fornisco io) ed iteri in quella folder path
- **2)** Vedi se c'è in quella folder path ci siano dei **file che finiscono con .txt**: 

- **3)** Se vedi la porzione finale del file contiene la stringa 
    **"all_th_level_4_std"** o 
    **all_th_level_5_std"**

   e se incontri queste stringhe, **escludi quei file .txt** e continua.. 

- **4)** Vedi invece se la porzione finale del file contiene la stringa **"_level_4_std"** o **"_level_5_std**:

- - **4.1.)** In quel caso, entri dentro quel file e **leggilo** ma poi fai una ulteriore considerazione, ossia
  - - vedi se quello che precede "_level_4_std" o "_level_5_std" sia **" th_"** dove * è un **suffisso dinamico**, che va da
      1 a 15...

Quindi avrai per ogni soggetto, due file .txt, che finiranno con questa stringa 

Per il **soggetto 1**: "**th_1_level_4_std**" o "**th_1_level_5_std**" 
Per il **soggetto 2**: "**th_2_level_4_std**" o "**th_2_level_5_std**" 

E così via, fino al 15° soggetto...

- **5)** Vedi in ognuna delle coppie di file .txt dello stesso soggetto
 
(i.e., ossia per esempio avrai per il soggetto 1 due file .txt, che finiranno con questa stringa 

"th_1_level_4_std" o "th_1_level_5_std" )

- **7)** Leggi il file .txt e vedi se ci sia un **riga in quel file .txt** con scritto 

**"Best Score for Window"**, seguito da **una sequenza di stringhe dinamica**, che cambia e che può essere presa da una lista di stringhe iterativamente che si costruisce a priori, del tipo:

"0-50" "25-75" etc., ossia che cambia di 25 valori ogni volta in maniera uniforme, quindi proseguendo sarebbe:
"50-100" "75-125" "100-150" "125-175" "150-200" "175-225" "200-250" "225-275" "250-300"

Quindi la lista di stringa dinamica potrebbe essere

**n_windows** = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"]

di conseguenza, itera per ogni elemento di questa lista "n_windows" per riconoscere se questa **sequenza di stringa dinamica** completi un riga dentro il file .txt che avrà scritto quindi:
 
**"Best Score for Window" + {elemento della lista "n_windows}**:"

A questo punto, avrai l'intera riga che sarà ad esempio:

"Best Score for Window 0-50: ".. 

In quella stessa riga del file .txt, dovresti trovare un **valore float**.. 

- **8)** Vorrei che prendessi quel valore float e **lo appendessi ad un dizionario**, che conterrà nei suoi vari valori i vari **best score ottenuti da quel soggetto lì, per ciascuna delle finestra considerate**
(che vanno da 0-50 a 250-300, ossia prendendo a riferimento quello che c'è dentro "n_windows"

'n_windows = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"])

Questo dizionario la chiamerò ad esempio **"best_scores_level_4_single_th"**, che ad esempio avrà, 

come primo "valore", la chiave associata al primo soggetto (i.e, **th_1**)

il quale poi avrà 

- - **A)** come sotto-chiave il nome dell'elemento iterato rispetto a "n_windows" e 
- - **B)** come sotto-valore il valore float associato al best score trovato per quella finestra lì, per quel soggetto lì, del tipo

**th_1** =  {'**0-50**': valore float del best score ottenuto dal soggetto 1 sulla finestra 0-50,  
'25-75': valore float del best score ottenuto dal soggetto 1 sulla finestra 25-75... etc] 

quindi in sostanza, "**best_scores_level_4_single_th**" sarà un **dizionario annidato**, 

che conterrà altri dizionari, ognuno con il nome del soggetto e 
come sotto-chiave del sottodizionario il valore stringa di quella finestra, 
come sotto-valore, il valore di best score ottenuto da quel soggetto lì, per quella finestra testata, ognuno dopo l'altro ...

Infatti, percorrendo tutto il file .txt, avrai altre righe in cui potrebbe comparire questa sequenza di stringhe del tipo 

"Best Score for Window {elemento di n_windows} ".. 

Quindi, alla fine, creerò un numero di dizionari pari al numero di soggetti, ossia 

th_1
th_2
th_3
th_4
th_5
th_6
th_7
th_8
th_9
th_10
th_11
th_12
th_13
th_14
th_15

dove ciascuna conterrà il numero di finestre per cui ho calcolato il best score, che sarà diversa per ogni finestra ovviamente...

quindi del tipo avrò questa costruzione di questi dizionari:

0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121

ognuna, quindi, dovrà conteggiare 

i best score ottenuti da ogni singolo soggetto, 
per quella finestra di segnale EEG, 
per il livello di ricostruzione considerato 

(che è identificato dall'aver visto se la porzione finale della stringa associata al nome del file contenga la stringa "_level_4_std" o "_level_5_std, quando iteri dentro la folder path)...


<br>

La stessa sequenza di passaggi vorrei che venisse eseguita quando si controlla che la porzione finale della stringa associata al nome del file contenga la stringa "_level_5_std" ...

quindi in quel caso creerò dizionario **best_scores_level_4_single_th**, con dentro una stessa struttura ossia


th_1
th_2
th_3
th_4
th_5
th_6
th_7
th_8
th_9
th_10
th_11
th_12
th_13
th_14
th_15


ognuna con dentro 


0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121




<br>

Quindi che nel codice voglio che si prenda dal relativo file .txt del soggetto 

(per i due livelli di ricostruzione del segnale, ossia ad esempio dal primo soggetto 

"optimized_params_th_1_level_4_std.txt"
e 
"optimized_params_th_1_level_5_std.txt"

per ogni finestra considerata
(i.e., n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"])

il migliore best score che il soggetto 1 ha ottenuto quella finestra lì, ossia per la prima che sarà 0-50
e così via per le altre...

e che la stessa cosa la deve fare per ogni soggetto (th_2, th_3 etc.)


<br>
<br>
<br>


**N.B. INTEGRAZIONE AGGIUNTIVA** 

Inoltre, quello che vorrei fare io è 

1) Per **ogni soggetto**, segnarmi
  - 1.1) il **valore di best score** per quella **specifica finestra** là,
  - 1.2) la **media dei punteggi** ottenuti in quella **specifica finestra** là .
  - 1.3.) la **relativa deviazione standard** di quel best score, **rispetto a quella finestra di quel soggetto specifico**..


Perché forse così ottengo una indicazione migliore di quanto è attendibile quel punteggio per quella finestra là, per quel soggetto lì... ma solo per quel soggetto lì, ossia srebbe una deviazione standard di quella finestra, ma soggetto-specifica... giusto?


Ossia, voglio ottenere una **misura di attendibilità specifica per ogni soggetto**. 

Quindi, stai cercando di **calcolare la deviazione standard dei punteggi di best score ottenuti per ciascuna finestra di un soggetto specifico**, tra tutte le combinazioni di iper-parametri testate. 

Questo darà **un'idea di quanto varia il miglior punteggio ottenuto per quella finestra per quel soggetto**.


STEPS :

- Estrai i punteggi migliori per ogni finestra e soggetto: Raccogli i punteggi migliori ottenuti per ciascuna finestra da tutte le combinazioni testate per quel soggetto.

- Calcola la deviazione standard per ciascuna finestra e soggetto: Per ogni finestra e soggetto, calcola la deviazione standard dei punteggi migliori ottenuti dai diversi modelli. Questo ti darà una misura di quanto varia il miglior punteggio ottenuto per quella finestra.


**OBIETTIVO**

La relazione che ti interessa è 

**come il best score si confronta con la deviazione standard rispetto al punteggio medio nella finestra. 
In altre parole, vuoi capire se il best score è significativamente alto rispetto alla variabilità (deviazione standard) dei punteggi in quella finestra**


<br>


**IMPLEMENTAZIONE**

Nel file .txt ci sono delle righe  che iniziano con 

"Window 0-50	Tested Params":  dove "0-50" è una stringa dinamica, che cambia in funzione della stringa iterata dentro la variabile "n_windows" ...


ora, se trovi nella riga questa sequenza di stringhe del tipo
"Window 0-50	Tested Params" .. voglio che prendi il valore float che, in quella riga, compare dopo la scritta 'Score:'..

quel valore corrisponde al valore di score ottenuto dal modello per quella combinazione di iper-parametri testata in quel momento lì...

tu dovresti avere alla fine 100 valori di score 

(in questo caso nel file .txt dalla riga 3 alla riga 102 se il pattern di riga corrisponde a "Window 0-50	Tested Params" dove  abbiamo detto che "0-50" è una stringa dinamica, che cambia in funzione della stringa iterata dentro la variabile "n_windows" ... )  

tutti questi valori, vorrei che li appendessi in una variabile che chiameremo scores_window_{n_window} dove "{n_window}" dovrebbe corrispondere al suffisso dinamico (ossia la stringa) che dipende dalla stringa iterata dentro la variabile "n_windows"..

Quindi, in questo caso, la variabile sarebbe "scores_window_0-50" e questa conterrà tutti i valori di score rispetto ai 100 modelli ottenuti per quella finestra "0-50", compreso anche il valore di best score per ottenuto per quella finestra 0-50 per lo specifico soggetto...

ora, da questa lista "scores_window_0-50", vorrei che mi calcolassi la media e la deviazione standard..

dove il valore di media lo salverai un nuova chiave del dizionario annidato... 

ossia,
ora ad esempio hai che nel codice le chiavi di primo ordine di 

"best_scores_level_4_single_th" sono:

best_scores_level_4_single_th keys: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

quindi, dentro ad esempio al sotto-dizionario del soggetto 1 (i..e, 'th_1') oltre alle sue sotto-chiavi che contengono il best score associato a quella finestra ossia ad esempio per il primo soggetto avrai 

0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121


vorrei che mettessi un'altra chiave, che chiamerai "mean_score_window_{n_window}" dove come sempre  "{n_window}" dovrebbe corrispondere al suffisso dinamico (ossia la stringa) che dipende dalla stringa iterata dentro la variabile "n_windows".. e quindi in questo primo caso sarebbe 
  
"mean_score_window_0-50" e dentro questa chiave, voglio che tu inserisce il valore di media calcolato sui valori di score ottenuti dal soggetto 1 per la finestra 0-50, 

e la stessa cosa, per la deviazione standard, che chiamerai

"std_score_window_0-50" e dentro questa chiave, voglio che tu inserisci la deviazione standard calcolata sui valori di score ottenuti dal soggetto 1 per la finestra 0-50...

tutta questa procedura, vorrei che la facessi per tutte le finestre, di ogni soggetto..

in modo che, dentro ogni sotto-dizionario di ogni soggetto , ossia per ogni chiave di primo ordine di 

best_scores_level_4_single_th keys: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

tu inserisca altre due chiavi, accanto a quelle che già contengono il valore di best score ottenuto da quel soggetto per quella finestra, ad esempio

0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121


ci metterai accanto anche la chiave associata alla media dei valori di score per quella finestra e della deviazione standard, ossia del tipo

"th_1":

0-50: 0.2681818181818182
"mean_score_window_0-50": valore float calcolato
"std_score_window_0-50": valore float calcolato

25-75: 0.2681818181818182
"mean_score_window_25-75": valore float calcolato
"std_score_window_25-75": valore float calcolato

....

e così via...

<br>
<br>
<br>


Dobbiamo 

1) iterare tra i file per ciascun soggetto,
2) cercare le righe con il pattern dinamico Window {window} Tested Params,
3) estrarre i valori di score associati e calcolare media e deviazione standard per ciascuna finestra di tempo.
4) Questi valori verranno aggiunti come nuove chiavi nel dizionario per ogni soggetto.

Ecco come possiamo aggiornare il codice:

- Cercare le righe con "Window {window} Tested Params" ed estrarre i valori di score.
- Memorizzare i valori dei punteggi in una lista.
- Calcolare la media e la deviazione standard per ciascuna finestra.
- Aggiungere questi valori nel dizionario per ogni soggetto.



##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI - OLD VERSION** 

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

In [ ]:
'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_th = {}
    best_scores_level_5_single_th = {}
    best_scores_level_5_detail_th = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "all_th_level_4_std" in file_name or "all_th_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            #if level == 4 and subject not in best_scores_level_4_single_th:
            
            if level == 'approx_4' and subject not in best_scores_level_4_single_th:    
                best_scores_level_4_single_th[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_th:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_th:
                best_scores_level_5_single_th[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_th:
                best_scores_level_5_detail_th[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_th[subject][window] = max(best_scores_level_4_single_th[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_th[subject][window] = max(best_scores_level_5_single_th[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_th[subject][window] = max(best_scores_level_5_detail_th[subject][window], best_score)

    return best_scores_level_4_single_th, best_scores_level_5_single_th, best_scores_level_5_detail_th  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_th_lr, best_scores_level_5_single_th_lr, best_scores_level_5_detail_th_lr = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_th_lr keys\033[0m: {best_scores_level_4_single_th_lr.keys()}")

for th_key, window_key in best_scores_level_4_single_th_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_th_lr keys\033[0m: {best_scores_level_5_single_th_lr.keys()}")

for th_key, window_key in best_scores_level_5_single_th_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_th_lr keys\033[0m: {best_scores_level_5_detail_th_lr.keys()}")

for th_key, window_key in best_scores_level_5_detail_th_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
import pickle

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_level_4_single_th_lr.pkl', 'wb') as file:
    pickle.dump(best_scores_level_4_single_th_lr, file)
    
# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_level_5_single_th_lr.pkl', 'wb') as file:
    pickle.dump(best_scores_level_5_single_th_lr, file)
    
# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_level_5_detail_th_lr.pkl', 'wb') as file:
    pickle.dump(best_scores_level_5_detail_th_lr, file)    


##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER EEG 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_th = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_th:    
                best_scores_filtered_1_20_single_th[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_th[subject][window] = max(best_scores_filtered_1_20_single_th[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_th

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_th_lr = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_th_lr keys\033[0m: {best_scores_filtered_1_20_single_th_lr.keys()}")

for th_key, window_key in best_scores_filtered_1_20_single_th_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
#pwd
#cd ..
#cd New_Plots_Sliding_Estimator_MNE

#path corretta --> cd Plots_Sliding_Estimator_MNE
#path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"

#Comandi da eseguire

#!pwd
#cd Plots_Sliding_Estimator_MNE


import pickle

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_filtered_1_20_single_th_lr.pkl', 'wb') as file:
    pickle.dump(best_scores_filtered_1_20_single_th_lr, file)

#print("Dati concantenati dei Singoli Terapisti salvati in 'subject_level_concatenations_th_1_20.pkl'")


##### **Descrizione degli step nel codice per plottare le best score performances per il level 4 e 5 dalle ricostruzioni**:

###### **Arrangement of Data Structure for EACH SINGLE Therapist's(TH01) accuracy score** 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ and δ)**

Adesso per ogni soggetto dentro i due dizionari annidati, ossia

**best_scores_level_4_single_th_lr** e **best_scores_level_5_single_th_lr**

voglio fare il plot che grafichi le accuratezze per ogni finestra testata di ogni soggetto.. 

Vorrei però chiederti delle modifiche, rispetto a queste modifiche che erano state fatte inizialmente, ossia:

1) Conversione dell'asse 𝑥: l'asse 𝑥 è stato generato per riflettere i millisecondi spostati di -200 ms.
2) Annotazioni sui punti temporali: le annotazioni mostrano i campioni temporali originali
3) Linea tratteggiata: Indica il 50° campione come inizio del periodo di prestimolo.


In ordine:

1) lascialo così, non toccarla

2) anziché le annotazioni che indicano il punto temporale che identifica l'inizio di ogni finestra, vorrei che mi segnassi con un carattere speciale "orizzontale" , tipo "-" il campione associato all'inizio e alla fine di ogni finestra, in modo che ci sia la corrispondenza del campione discretizzato EEG con il relativo tempo in misura di millisecondi...

tieni presente però che, 

lo spostamento di ogni finestra analizzata copre la metà della finestra precedente, perché l'intera finestra sarebbe di 50 campioni (che convertito son 200 mms), ma poi la finestra "successiva" comincia dopo i primi 25 campioni di quella precedente (quindi a metà di quella precedente!)

Ad esempio: 

La prima finestra, parte sull'asse x dal tempo 0 mms fino a 200 mms (per i primi 50 campioni discretizzati EEG)

La seconda finestra partirà dal 25° campione (quindi a metà della precedente finestra) e finirà 25 campioni (ossia 100 mms dopo) dopo la fine della prima finestra...

Quindi, devi trovare un modo di plottarmi un carattere speciale "orizzontale" , tipo "-", 

per indicare il campione associato all'inizio e alla fine di ogni finestra, tenendo conto di questa "parziale" sovrapposizione delle finestre tra di loro

inoltre, per ogni finestra, alla sua metà, disegnami un punto, 
che indicherà il valore di best score associato a quella finestra là.. 

ovviamente, tieni conto della collocazione grafica diversa (non sovrapposta) tra 

il punto che identifica il valore di best score per quella finestra lì, con 
il carattere speciale "orizzontale" , tipo "-" che rappresenterà il campione  associato all'inizio della finestra successiva...


<br>

#### Comments on Edits:


- Le annotazioni sui punti temporali adesso utilizzano un carattere speciale "orizzontale" (-) per indicare l'inizio e la fine di ogni finestra (50 campioni), considerando la sovrapposizione parziale.
  
- Viene tracciato un punto centrale per ogni finestra, che rappresenta il valore di best score per quella finestra.

- Il carattere speciale "orizzontale" viene posizionato per evitare sovrapposizioni con i punti che indicano i valori di best score.



##### **ALL SINGLE Therapists (TH01-TH20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI - OLD VERSION**

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX & LEVEL 5 DA COEFF DETAIL DELLE RICOSTRUZIONI**

In [ ]:
!pwd

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

In [ ]:
#new_subject_level_concatenations_th.keys()

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO TERAPISTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI APPROX 4, APPROX 5 e DETAIL 5

best_scores_level_4_single_th_lr, 
best_scores_level_5_single_th_lr,
best_scores_level_5_detail_th_lr
'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
     # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    ths_baseline_accuracy_highest_class_in_fold_lr = list()
    
    for subject, scores in best_scores_dict.items():
        
        '''Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_th:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_th[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            ths_baseline_accuracy_highest_class_in_fold_lr.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        

        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'approx_4':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta'
            clf_str = 'lr'
            
        elif level == 'approx_5':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            
            level_str = 'delta'
            clf_str = 'lr'
                
                
        elif level == 'detail_5':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta_strict'
            clf_str = 'lr'
            
        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='g', zorder=5, label=f'Best Score Logistic Regression for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='g', zorder=5, label=f'Best Score Logistic Regression for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return ths_baseline_accuracy_highest_class_in_fold_lr

# Esempio di utilizzo
save_path_level_4 = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5 = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5_detail = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
ths_baseline_accuracy_highest_class_in_fold_level_4_lr = plot_best_scores_for_subjects(best_scores_level_4_single_th_lr, 'approx_4', save_path_level_4)
ths_baseline_accuracy_highest_class_in_fold_level_5_lr = plot_best_scores_for_subjects(best_scores_level_5_single_th_lr, 'approx_5', save_path_level_5)
ths_baseline_accuracy_highest_class_in_fold_level_5_detail_lr = plot_best_scores_for_subjects(best_scores_level_5_detail_th_lr, 'detail_5', save_path_level_5)

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd Plots_Sliding_Estimator_MNE/

In [ ]:
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl


# Salvare l'intero dizionario annidato con pickle
#import pickle

#with open(path + 'ths_baseline_accuracy_highest_class_in_fold_lr.pkl', 'wb') as f:
#pickle.dump(best_scores_level_4_single_th_lr, f)
    

#path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'

# Salvare l'intero dizionario annidato con pickle
import pickle

with open('best_scores_level_4_single_th_lr.pkl', 'wb') as f:
    pickle.dump(best_scores_level_4_single_th_lr, f)

with open('best_scores_level_5_single_th_lr.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_single_th_lr, f)
    
with open('best_scores_level_5_detail_th_lr.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_detail_th_lr, f)
    
    
# Caricare il dizionario salvato con pickle
#import pickle 

#with open('/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations_th.pkl', 'rb') as f:
#    subject_level_concatenations_th = pickle.load(f)

###### **Additional Edits for plots (Skip Now)**

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
!pwd

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)

In [ ]:
#new_subject_level_concatenations_th_1_20.keys()
#dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16'])

#new_subject_level_concatenations_th_1_20['th_16'].keys()
#dict_keys(['data', 'labels'])

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO TERAPISTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI FILTERED 1-20Hz

best_scores_filtered_1_20_single_th_lr

'''


import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
     # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots_1_20')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    ths_baseline_accuracy_highest_class_in_fold_lr = list()
    
    for subject, scores in best_scores_dict.items():
        
        ''' Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}_filtered_1_20')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_th_1_20:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_th_1_20[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            ths_baseline_accuracy_highest_class_in_fold_lr.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        
        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'filtered_1_20':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)',  fontsize = 16)
            
            level_str = 'filtered_1_20'
            clf_str = 'lr'
            

        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='g', zorder=5, label=f'Best Score Logistic Regression for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subj {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='g', zorder=5, label=f'Best Score Logistic Regression for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subj {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return ths_baseline_accuracy_highest_class_in_fold_lr

# Esempio di utilizzo
save_path_filtered_1_20 = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
ths_baseline_accuracy_highest_class_in_fold_1_20_lr = plot_best_scores_for_subjects(best_scores_filtered_1_20_single_th_lr, 'filtered_1_20', save_path_filtered_1_20)


#### **All Therapists (TH01-TH20)**

#### Plots of **Grand Average Mean** of Best Single Subject's Accuracy Score Performances 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **Istruzioni per il codice**

Fammi un codice python che faccia queste cose 

- **1)** Entrami in una **folder path** (che ti fornisco io) ed iteri in quella folder path
- **2)** Vedi se c'è in quella folder path ci siano dei **file che finiscono con .txt**: 

- **3)** Se vedi la porzione finale del file contiene la stringa 
    **"all_th_level_4_std"** o 
    **all_th_level_5_std"**

   e se incontri queste stringhe, **escludi quei file .txt** e continua.. 

- **4)** Vedi invece se la porzione finale del file contiene la stringa **"_level_4_std"** o **"_level_5_std**:

- - **4.1.)** In quel caso, entri dentro quel file e **leggilo** ma poi fai una ulteriore considerazione, ossia
  - - vedi se quello che precede "_level_4_std" o "_level_5_std" sia **" th_"** dove * è un **suffisso dinamico**, che va da
      1 a 15...

Quindi avrai per ogni soggetto, due file .txt, che finiranno con questa stringa 

Per il **soggetto 1**: "**th_1_level_4_std**" o "**th_1_level_5_std**" 
Per il **soggetto 2**: "**th_2_level_4_std**" o "**th_2_level_5_std**" 

E così via, fino al 15° soggetto...

- **5)** Vedi in ognuna delle coppie di file .txt dello stesso soggetto
 
(i.e., ossia per esempio avrai per il soggetto 1 due file .txt, che finiranno con questa stringa 

"th_1_level_4_std" o "th_1_level_5_std" )

- **7)** Leggi il file .txt e vedi se ci sia un **riga in quel file .txt** con scritto 

**"Best Score for Window"**, seguito da **una sequenza di stringhe dinamica**, che cambia e che può essere presa da una lista di stringhe iterativamente che si costruisce a priori, del tipo:

"0-50" "25-75" etc., ossia che cambia di 25 valori ogni volta in maniera uniforme, quindi proseguendo sarebbe:
"50-100" "75-125" "100-150" "125-175" "150-200" "175-225" "200-250" "225-275" "250-300"

Quindi la lista di stringa dinamica potrebbe essere

**n_windows** = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"]

di conseguenza, itera per ogni elemento di questa lista "n_windows" per riconoscere se questa **sequenza di stringa dinamica** completi un riga dentro il file .txt che avrà scritto quindi:
 
**"Best Score for Window" + {elemento della lista "n_windows}**:"

A questo punto, avrai l'intera riga che sarà ad esempio:

"Best Score for Window 0-50: ".. 

In quella stessa riga del file .txt, dovresti trovare un **valore float**.. 

- **8)** Vorrei che prendessi quel valore float e **lo appendessi ad un dizionario**, che conterrà nei suoi vari valori i vari **best score ottenuti da quel soggetto lì, per ciascuna delle finestra considerate**
(che vanno da 0-50 a 250-300, ossia prendendo a riferimento quello che c'è dentro "n_windows"

'n_windows = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"])

Questo dizionario la chiamerò ad esempio **"best_scores_level_4_single_th"**, che ad esempio avrà, 

come primo "valore", la chiave associata al primo soggetto (i.e, **th_1**)

il quale poi avrà 

- - **A)** come sotto-chiave il nome dell'elemento iterato rispetto a "n_windows" e 
- - **B)** come sotto-valore il valore float associato al best score trovato per quella finestra lì, per quel soggetto lì, del tipo

**th_1** =  {'**0-50**': valore float del best score ottenuto dal soggetto 1 sulla finestra 0-50,  
'25-75': valore float del best score ottenuto dal soggetto 1 sulla finestra 25-75... etc] 

quindi in sostanza, "**best_scores_level_4_single_th**" sarà un **dizionario annidato**, 

che conterrà altri dizionari, ognuno con il nome del soggetto e 
come sotto-chiave del sottodizionario il valore stringa di quella finestra, 
come sotto-valore, il valore di best score ottenuto da quel soggetto lì, per quella finestra testata, ognuno dopo l'altro ...

Infatti, percorrendo tutto il file .txt, avrai altre righe in cui potrebbe comparire questa sequenza di stringhe del tipo 

"Best Score for Window {elemento di n_windows} ".. 

Quindi, alla fine, creerò un numero di dizionari pari al numero di soggetti, ossia 

**th_1**
**th_2**
**th_3**
**th_4**
**th_5**
**th_6**
**th_7**
**th_8**
**th_9**
**th_10**
**th_11**
**th_12**
**th_13**
**th_14**
**th_15**

dove ciascuna conterrà il numero di finestre per cui ho calcolato il best score, che sarà diversa per ogni finestra ovviamente...

quindi del tipo avrò questa costruzione di questi dizionari:

**0-50**: 0.2681818181818182
**25-75**: 0.2681818181818182
**50-100**: 0.2681818181818182
**75-125**: 0.2621212121212121
**100-150**: 0.2621212121212121
**125-175**: 0.2621212121212121
**150-200**: 0.2621212121212121
**175-225**: 0.2621212121212121
**200-250**: 0.2681818181818182
**225-275**: 0.2621212121212121
**250-300**: 0.2621212121212121

ognuna, quindi, dovrà conteggiare 

i best score ottenuti da ogni singolo soggetto, 
per quella finestra di segnale EEG, 
per il livello di ricostruzione considerato 

(che è identificato dall'aver visto se la porzione finale della stringa associata al nome del file contenga la stringa "_level_4_std" o "_level_5_std, quando iteri dentro la folder path)...


<br>

La stessa sequenza di passaggi vorrei che venisse eseguita quando si controlla che la porzione finale della stringa associata al nome del file contenga la stringa "_level_5_std" ...

quindi in quel caso creerò dizionario **best_scores_level_4_single_th**, con dentro una stessa struttura ossia


th_1
th_2
th_3
th_4
th_5
th_6
th_7
th_8
th_9
th_10
th_11
th_12
th_13
th_14
th_15


ognuna con dentro 


0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121




<br>

Quindi che nel codice voglio che si prenda dal relativo file .txt del soggetto 

(per i due livelli di ricostruzione del segnale, ossia ad esempio dal primo soggetto 

"optimized_params_th_1_level_4_std.txt"
e 
"optimized_params_th_1_level_5_std.txt"

per ogni finestra considerata
(i.e., n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"])

il migliore best score che il soggetto 1 ha ottenuto quella finestra lì, ossia per la prima che sarà 0-50
e così via per le altre...

e che la stessa cosa la deve fare per ogni soggetto (th_2, th_3 etc.)


<br>
<br>
<br>


**N.B. INTEGRAZIONE AGGIUNTIVA PER ANALISI DI MEDIA GLOBALE!** 

Inoltre, quello che vorrei fare io è 

1) Per **ogni soggetto**, segnarmi
  - 1.1) il **valore di best score** per quella **specifica finestra** là,
  - 1.2) la **media dei punteggi** ottenuti in quella **specifica finestra** là .
  - 1.3.) la **relativa deviazione standard** di quel best score, **rispetto a quella finestra di quel soggetto specifico**..


Perché forse così ottengo una indicazione migliore di quanto è attendibile quel punteggio per quella finestra là, per quel soggetto lì... ma solo per quel soggetto lì, ossia srebbe una deviazione standard di quella finestra, ma soggetto-specifica... giusto?


Ossia, voglio ottenere una **misura di attendibilità specifica per ogni soggetto**. 

Quindi, stai cercando di **calcolare la deviazione standard dei punteggi di best score ottenuti per ciascuna finestra di un soggetto specifico**, tra tutte le combinazioni di iper-parametri testate. 

Questo darà **un'idea di quanto varia il miglior punteggio ottenuto per quella finestra per quel soggetto**.


STEPS :

- Estrai i punteggi migliori per ogni finestra e soggetto: Raccogli i punteggi migliori ottenuti per ciascuna finestra da tutte le combinazioni testate per quel soggetto.

- Calcola la deviazione standard per ciascuna finestra e soggetto: Per ogni finestra e soggetto, calcola la deviazione standard dei punteggi migliori ottenuti dai diversi modelli. Questo ti darà una misura di quanto varia il miglior punteggio ottenuto per quella finestra.


**OBIETTIVO**

La relazione che ti interessa è 

**come il best score si confronta con la deviazione standard rispetto al punteggio medio nella finestra. 
In altre parole, vuoi capire se il best score è significativamente alto rispetto alla variabilità (deviazione standard) dei punteggi in quella finestra**





**match = re.search(rf"{pattern}\s+([0-9]** * **\.?[0-9]+)",line)**


Serve per cercare all'interno di una stringa (line) un pattern specifico e, se trovato, estrae un numero in formato float dalla stringa.

<br>

**Dettagli della riga**:

- **re.search()**: Questa funzione di Python appartiene al modulo re, che si usa per eseguire operazioni con espressioni regolari (regex). La funzione cerca una corrispondenza all'interno di una stringa. Se trova una corrispondenza, restituisce un oggetto Match; altrimenti, restituisce None.

rf"{pattern}\s+([0-9]*\.?[0-9]+)": Questa è un'espressione regolare, ed è composta da diverse parti:

- **rf**: Significa "raw formatted string". Il prefisso r indica una "raw string", che dice a Python di non interpretare caratteri speciali come \ ma di passarli direttamente all'espressione regolare. Il prefisso f permette di inserire variabili nella stringa usando le parentesi graffe {}.

- **{pattern}**: È una variabile che contiene una stringa (in questo caso f"Best Score for Window {window}:"). Quindi, per esempio, potrebbe diventare "Best Score for Window 0-50:".
\s+: Questo significa "uno o più spazi bianchi" (spazi, tab, ecc.). Indica che dopo il pattern può esserci uno o più spazi prima del numero.

- **([0-9]*\.?[0-9]+)**: Questo è il pattern che identifica un numero in formato float.

<br>

Vediamolo in dettaglio:

- [0-9]*: cerca zero o più cifre (quindi permette che il numero inizi senza zeri).
\.?: cerca un punto decimale opzionale (il punto . è un carattere speciale nelle regex, quindi va preceduto da un backslash \).
- [0-9]+: cerca una o più cifre dopo il punto decimale (se presente).
- 
Complessivamente, questo pattern cerca un numero che può essere intero o decimale.

- **line**: È la stringa (riga di testo) in cui viene cercato il pattern. Nel tuo caso, line rappresenta ogni riga del file .txt che viene processata.

**Risultato (match)**: Se l'espressione regolare trova una corrispondenza (ovvero, se esiste una riga che contiene la stringa "Best Score for Window X-Y:" seguita da un numero float), re.search() restituisce un oggetto Match che contiene le informazioni della corrispondenza. Se non trova nulla, restituisce None.

<br>

**Esempio pratico**:
Supponiamo che pattern sia "Best Score for Window 0-50:" e che line contenga la seguente stringa:


"Best Score for Window 0-50: 0.85"

L'espressione regolare cercherà:

- "Best Score for Window 0-50:" (contenuto in pattern),
- poi uno o più spazi bianchi (\s+),
- e infine un numero float (([0-9]*\.?[0-9]+)), in questo caso 0.85.

Se viene trovata una corrispondenza, l'oggetto Match conterrà il numero 0.85.

Quindi, match.group(1) restituirà il numero 0.85 come stringa, che poi viene convertito in float

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI** - **OLD VERSION**

Ora vorrei che **per ogni dizionario**, per **ogni elemento di ogni dizionario** (ogni lista), vorrei che 

- mi calcolassi **la media** e la **deviazione standard** e
- me le **salvassi come ulteriori chiavi di quel dizionario lì**, col nome di chiave relativo alla lista da cui stai prendendo i valori float.

<br>

Esempio pratico:

Dalla chiave **"0-50"** calcolerai 
- la media
- la deviazione standard di quei valori lì

- E poi la media e la media e deviazione standard **li salvi dentro altre due
chiavi**:
  - una che si chiamerà **"mean_0-50_level_4**"
  - l'altra **"std_0-50_level_4"**


E così via **per tutte le altre finestre**, e **per entrambi i dizionari**, ossia 
- sia per **"all_th_best_scores_level_4"**
- sia per **"all_th_best_scores_level_5"**..

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE E PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **NEW VERSION**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_th = {}
    best_scores_level_5_single_th = {}
    best_scores_level_5_detail_th = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "all_th_level_4_std" in file_name or "all_th_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            #if level == 4 and subject not in best_scores_level_4_single_th:
            
            if level == 'approx_4' and subject not in best_scores_level_4_single_th:    
                best_scores_level_4_single_th[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_th:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_th:
                best_scores_level_5_single_th[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_th:
                best_scores_level_5_detail_th[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_th[subject][window] = max(best_scores_level_4_single_th[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_th[subject][window] = max(best_scores_level_5_single_th[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_th[subject][window] = max(best_scores_level_5_detail_th[subject][window], best_score)

    return best_scores_level_4_single_th, best_scores_level_5_single_th, best_scores_level_5_detail_th  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_th_lr, best_scores_level_5_single_th_lr, best_scores_level_5_detail_th_lr = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultat
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_th_lr keys\033[0m: {best_scores_level_4_single_th_lr.keys()}")

for th_key, window_key in best_scores_level_4_single_th_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_th_lr keys\033[0m: {best_scores_level_5_single_th_lr.keys()}")

for th_key, window_key in best_scores_level_5_single_th_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_th_lr keys\033[0m: {best_scores_level_5_detail_th_lr.keys()}")

for th_key, window_key in best_scores_level_5_detail_th_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        '''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")
        
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_4 = calculate_mean_and_confidence_interval(best_scores_level_4_single_th_lr, n_windows)
statistics_level_5 = calculate_mean_and_confidence_interval(best_scores_level_5_single_th_lr, n_windows)
statistics_level_5_detail = calculate_mean_and_confidence_interval(best_scores_level_5_detail_th_lr, n_windows)

In [ ]:
'''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
#print(best_scores_level_4_single_th_lr['th_1']['0-50'])
#print(best_scores_level_4_single_th_lr['th_2']['0-50'])
#print(best_scores_level_4_single_th_lr['th_3']['0-50'])
#print()
#print(best_scores_level_4_single_th_lr['th_1']['25-75'])
#print(best_scores_level_4_single_th_lr['th_2']['25-75'])
#print(best_scores_level_4_single_th_lr['th_3']['25-75'])

In [ ]:
type(statistics_level_4)

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
!pwd

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('new_all_th_concat_reconstructions.pkl', 'rb') as f:
    new_all_th_concat_reconstructions = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_th['th_1'].keys()

In [ ]:
new_all_th_concat_reconstructions.keys()

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('new_all_th_concat_reconstructions.pkl', 'rb') as f:
    new_all_th_concat_reconstructions = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_th.keys()

In [ ]:
new_subject_level_concatenations_th['th_1'].keys()

In [ ]:
new_all_th_concat_reconstructions.keys()

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    subjects_dir = os.path.join(save_path, f'plot_mean_all_ths_level_{level}')
    os.makedirs(subjects_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 4:
        level_str = 'theta'
    elif level == 5:
        level_str = 'delta'
    elif level == '5_detail':
        level_str = 'theta_strict'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'all_ths_level_{level_str}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    print(f"\n\t\t\t\t\t\033[1mTherapists'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_th_concat_reconstructions.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    
    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)

    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Aggiunge il livello di baseline in base al livello specificato
    #if level == 4:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range')
    #elif level == 5:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range')
    #elif level == '5_detail':
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Detail Range')
    
    '''VECCHIO'''
    
    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
    if level_str == 'theta':
        ax1.set_title(f'Logistic Regression - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range', fontsize = 16)
        ax2.set_title(f'Logistic Regression - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range', fontsize = 16)
        
    elif level_str == 'delta':
        ax1.set_title(f'Logistic Regression - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)
        ax2.set_title(f'Logistic Regression - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)

    elif level_str == 'theta_strict':
        ax1.set_title(f'Logistic Regression - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
        ax2.set_title(f'Logistic Regression - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
    
    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='g', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='g', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='g', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='g', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_ths_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(subjects_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_4, 4, save_path)
plot_mean_best_scores_for_window(statistics_level_5, 5, save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail, '5_detail', save_path)

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE E PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    

 # Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_all_th_concat_reconstructions_1_20.pkl', 'rb') as f:
    new_all_th_concat_reconstructions_1_20 = pickle.load(f)

In [ ]:
print(new_subject_level_concatenations_th_1_20.keys())
print()
print(new_subject_level_concatenations_th_1_20['th_1'].keys())
print(new_subject_level_concatenations_th_1_20['th_1']['data'].shape)
print()
print(new_all_th_concat_reconstructions_1_20.keys())
print(new_all_th_concat_reconstructions_1_20['data'].shape)

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''

import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_th = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_th:    
                best_scores_filtered_1_20_single_th[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_th[subject][window] = max(best_scores_filtered_1_20_single_th[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_th

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_th_lr = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_th_lr keys\033[0m: {best_scores_filtered_1_20_single_th_lr.keys()}")

for th_key, window_key in best_scores_filtered_1_20_single_th_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_1_20 = calculate_mean_and_confidence_interval(best_scores_filtered_1_20_single_th_lr, n_windows)

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    data_dir = os.path.join(save_path, f'plot_mean_all_ths_level_{level}')
    os.makedirs(data_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 'filtered_1_20':
        level_str = 'filtered_1_20'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    #print(f"\n\t\t\t\t\t\033[1mPatients'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_th_concat_reconstructions_1_20.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}\n\n\n")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    
    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)
    
    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Linea orizzontale per il chance level
    #plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    #plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)')

    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è filtered_1_20, gestisci i titoli per i grafici su ax1 e ax2
    if level == 'filtered_1_20':

        ax1.set_title(f'Logistic Regression - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
        ax2.set_title(f'Logistic Regression - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)

    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='g', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='g', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='g', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='g', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_ths_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(data_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'\nPlot salvato in: \n\033[1m{save_file_path}\033[0m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_1_20, 'filtered_1_20', save_path)

#### **ALL SINGLE Patients (PT01-PT20)**

#### Automatization of all steps from:

1) "**subject_level_concatenations_pt**" : ricostruzioni 4 e 5° livello wavelet da approx coefficients
2) "**new_subject_level_concatenations_pt**":  ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_pt_1_20**": EEG preprocessed signal filtered 1-20Hz 

In [ ]:
import pickle 

# Caricare il dizionario salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)
    
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations_pt.pkl

#import pickle
## Salvare l'intero dizionario annidato con pickle
#with open('subject_level_concatenations.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations, f)

#subject_level_concatenations_pt['pt_1'].keys()


# Caricare il dizionario salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    


In [ ]:
new_subject_level_concatenations_pt.keys()

In [ ]:
new_subject_level_concatenations_pt_1_20.keys()

##### **Descrizione degli step nel codice per ottenere e salvare nelle paths le best score performances per il level 4 e 5 dalle ricostruzioni**:

Vorrei in questo caso, per velocizzare, iterare su 

subject_level_concatenations, che ha questa struttura...

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


al cui interno ha per ogni chiave di primo ordine, un altro dizionario annidato, che è fatto di queste chiavi


dict_keys(['theta', 'delta', 'labels'])

dentro 'theta' e 'delta' ci sono tutti i dati di tutte le condizioni sperimentali del singolo soggetto

del tipo 'theta' o 'delta' conterrà un array con shape

(204, 3, 300)

con 1° dimensione i trial, poi i canali, poi i punti di ogni trial (campioni EEG)

e dentro 'labels' ho invece l'array delle labels concatenate...
(204,)


<br>


Ora però, vorrei che ... 

Se ad esempio nel soggetto 'th_1' entri nella chiave 'theta', 

allora poi il file corrispondente .txt deve essere scritto con una path dinamica, che cambia a seconda 
- sia del soggetto iterato
- sia del livello di ricostruzione dei dati

Ossia:

la "params_dir" è fissa

mentre 

"params_file_path" è dinamica, e cambia a seconda del soggetto iterato e del livello. 

Per cui sarà una composizione di stringhe fisse e stringhe 'mobili', ossia

'params_file_path' = 'optimized_params_' + {subject} dove subject dovrebbe essere una lista di stringhe che si preleva dalle chiavi di primo ordine di "subject_level_concatenations" che erano

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


seguito da "_level_{level}_std" dove {level} dipende dal nome della chiave del sotto-dizionario iterato per ogni soggetto...

Ossia, ad esempio dentro il sotto-dizionario del primo soggetto di "subject_level_concatenations" cioè

subject_level_concatenations['th_1'], 

Se la sua sotto-chiave è 'theta' allora il level = 4, se la chiave è 'delta' allora il level = 5, 



Quindi la costruzione finale della path dinamica del file specifico per il soggetto 1 deve essere

 
params_file_path = 'optimized_params_' +'{subject}' + "_level_{level}_std.txt"

e sarà se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_1' + "_level_4_std.txt"


e sarà se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_1' + "_level_5_std.txt"


in questo modo, farei un loop unico su tutte le sottochiavi dei dizionari annidati dentro 
"subject_level_concatenations" 

ossia 
dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

e per ognuno vedo se la sua sotto-chiave sarà 'theta' o 'delta' e creerà dei file .txt corrispondenti nella param_dir che gli ho chiesto...

Il resto del codice non toccarlo invece, perché dovrebbe creare dei file .txt per ogni soggetto per ogni livello di ricostruzione dei dati,
e salverà le analisi nel file .txt corrispondente



Ad esempio, continuando col soggetto 2:

la costruzione finale della path dinamica del file specifico per il soggetto 2

Sarà, se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_2' + "_level_4_std.txt"


e sarà, se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_2' + "_level_5_std.txt"


e così via per tutti gli altri soggetti




##### **ALL SINGLE Patients (PT01-PT15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DALLE RICOSTRUZIONI**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**


In [ ]:
''' PATIENTS

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., Θ+δ, Θ e δ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare

#Some penalties may not work with some solvers. 
#See the parameter solver below, to know the compatibility between the penalty and solver.


Per la classificazione multi-classe con l'opzione multi_class='multinomial', 
puoi utilizzare i seguenti solver e le relative penalità:

newton-cg: supporta solo l2 e None.
sag: supporta solo l2 e None.
saga: supporta l1, l2, elasticnet, e None.
lbfgs: supporta solo l2 e None.

Quindi, se vuoi esplorare solo il caso multinomiale, puoi utilizzare i seguenti abbinamenti di solver e penalità:

newton-cg: l2, None
sag: l2, None
saga: l1, l2, elasticnet, None
lbfgs: l2, None

'''

import numpy as np
import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER MULTINOMIAL LOGISTIC REGRESSION'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra penalty e solver, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...


# Definizione dei parametri validi, ossia delle coppie solver-penalty associate
params = {'newton-cg': ['l2', None],
    'sag': ['l2', None],
    'saga': ['l1', 'l2', 'elasticnet', None],
    'lbfgs': ['l2', None]
}


# Assicuriamoci di non avere duplicati e di avere una lista di dizionari separati per solver e penalty
parameters_dist = {
    'solver': list(params.keys()),
    'penalty': list(set(penalty for penalties in params.values() for penalty in penalties)),
    'C': [0.001, 0.01, 0.1, 1, 10, 100]
    
}

print(f"\033[1mparameters_dist\033[0m è: {parameters_dist}")

def generate_valid_params(params):
    valid_params = []
    
    # Generate values from 0 to 1 (inclusive) with step 0.05
    l1_ratio_values = np.append(np.arange(0.0, 1.0, 0.05), 1.0)

    # Impongo parametro C con valori su scala logaritmica 
    C_values = [0.001, 0.01, 0.1, 1, 10, 100]

    for C in C_values: 
        for solver in params['solver']:
            if solver == 'newton-cg':
                penalties = ['l2', None]
            elif solver == 'sag':
                penalties = ['l2', None]
            elif solver == 'lbfgs':
                penalties = ['l2', None]
            elif solver == 'saga':
                penalties = ['l1', 'l2', 'elasticnet', None]  # Include None here explicitly
            else:
                penalties = params['penalty']
            
            # Create parameter dictionaries for each combination of solver and penalty
            for penalty in penalties:
                if penalty == 'elasticnet':
                    for l1_ratio in l1_ratio_values:
                        valid_params.append({'solver': [solver], 'penalty': ['elasticnet'], 'l1_ratio': [l1_ratio], 'C': [C]})
                        
                else:
                    valid_params.append({'solver': [solver], 'penalty': [penalty], 'C': [C]})
    
    return valid_params


# Funzione per verificare se una combinazione di iperparametri è valida
def valid_param_combination(params):
    solver = params['solver']
    penalty = params['penalty']
    
    if solver in ['newton-cg', 'lbfgs', 'sag'] and penalty in ['l2', None]:
        return True
    elif solver == 'saga' and penalty in ['l1', 'l2', 'elasticnet', None]:
        return True
    else:
        return False

valid_params_list = generate_valid_params(parameters_dist)
print(f"\n\033[1mvalid_params_list\033[0m è: {valid_params_list}")




import numpy as np
import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER MULTINOMIAL LOGISTIC REGRESSION'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra penalty e solver, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...


# Definizione dei parametri validi, ossia delle coppie solver-penalty associate
params = {'newton-cg': ['l2', None],
    'sag': ['l2', None],
    'saga': ['l1', 'l2', 'elasticnet', None],
    'lbfgs': ['l2', None]
}


# Assicuriamoci di non avere duplicati e di avere una lista di dizionari separati per solver e penalty
parameters_dist = {
    'solver': list(params.keys()),
    'penalty': list(set(penalty for penalties in params.values() for penalty in penalties)),
    'C': [0.001, 0.01, 0.1, 1, 10, 100]
    
}

print(f"\033[1mparameters_dist\033[0m è: {parameters_dist}")

def generate_valid_params(params):
    valid_params = []
    
    # Generate values from 0 to 1 (inclusive) with step 0.05
    l1_ratio_values = np.append(np.arange(0.0, 1.0, 0.05), 1.0)

    # Impongo parametro C con valori su scala logaritmica 
    C_values = [0.001, 0.01, 0.1, 1, 10, 100]

    for C in C_values: 
        for solver in params['solver']:
            if solver == 'newton-cg':
                penalties = ['l2', None]
            elif solver == 'sag':
                penalties = ['l2', None]
            elif solver == 'lbfgs':
                penalties = ['l2', None]
            elif solver == 'saga':
                penalties = ['l1', 'l2', 'elasticnet', None]  # Include None here explicitly
            else:
                penalties = params['penalty']
            
            # Create parameter dictionaries for each combination of solver and penalty
            for penalty in penalties:
                if penalty == 'elasticnet':
                    for l1_ratio in l1_ratio_values:
                        valid_params.append({'solver': [solver], 'penalty': ['elasticnet'], 'l1_ratio': [l1_ratio], 'C': [C]})
                        
                else:
                    valid_params.append({'solver': [solver], 'penalty': [penalty], 'C': [C]})
    
    return valid_params


# Funzione per verificare se una combinazione di iperparametri è valida
def valid_param_combination(params):
    solver = params['solver']
    penalty = params['penalty']
    
    if solver in ['newton-cg', 'lbfgs', 'sag'] and penalty in ['l2', None]:
        return True
    elif solver == 'saga' and penalty in ['l1', 'l2', 'elasticnet', None]:
        return True
    else:
        return False

valid_params_list = generate_valid_params(parameters_dist)
#print(f"\n\033[1mvalid_params_list\033[0m è: {valid_params_list}")


# Itera attraverso i soggetti

'''OLD VERSION'''
#for subject, levels in subject_level_concatenations.items():

'''NEW VERSION'''
for subject, levels in new_subject_level_concatenations_pt.items():
    
    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO'''
    
    #if subject == 'pt_1':
    #if subject == 'pt_17' or subject == 'pt_18' or subject == 'pt_19':
    if subject == 'pt_20':

        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")


        '''NEW VERSION'''
        #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
        params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params'

        # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
        #                                      'delta' = δ,i.e., approx_5 ,
        #                                      'theta_strict' = Θ, i.e., detail_5,
        #                                      'labels') 

        for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'


            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")

            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_std.txt'

            #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\t\033[1m{params_dir}\033[0m"),
            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

            y = levels['labels'] # Estraiamo le labels livello corrente del soggetto corrente

            '''OLD VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            #params_dir = '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/prova'

            #FILE PATH DINAMICA PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            #A SECONDA DEL SOGGETTO E LIVELLO DI RICOSTRUZIONE DEI DATI PRESI IN ESAME 

            # Costruzione del percorso del file in maniera dinamica
            #params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_std.txt'

            #if not os.path.exists(params_dir):
            #    os.makedirs(params_dir)

            #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\t\033[1m{params_dir}\033[0m"),
            #print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE LOGISTIC REGRESSION

            # Inizializzo modello Logistic Regression base (da sklearn.LinearModel version 1.0.5)
            log_reg_base = LogisticRegression(class_weight = class_weight_dict, max_iter = 20000)

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni istante temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0


            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")


            '''INIZIALIZZAZIONE RANDOM SEARCH'''

            # Inizializzazione della Random Search:

            #https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

            #cv: int, cross-validation generator or an iterable, default=None
            #Determines the cross-validation splitting strategy. 

            #Possible inputs for cv are:

            #None, to use the default 5-fold cross validation,
            #integer, to specify the number of folds in a (Stratified)KFold,
            #CV splitter,
            #An iterable yielding (train, test) splits as arrays of indices.

            #random_state: int, RandomState instance or None, default=None
            #Pseudo random number generator state used for random uniform sampling from lists of possible values 
            #instead of scipy.stats distributions. Pass an int for reproducible output across multiple function calls

            # RandomizedSearchCV è una tecnica di ricerca iperparametrica che 
            # campiona casualmente combinazioni di iperparametri da un insieme predefinito.

            #n_iter determina il numero di combinazioni di iperparametri da testare durante la ricerca


            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1



            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                #print(X_window_reshaped.shape)

                #Da https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

                #param_distributions: 

                #Dictionary with parameters names (str) as keys and distributions or lists of parameters to try. 
                #Distributions must provide a rvs method for sampling (such as those from scipy.stats.distributions). 
                #If a list is given, it is sampled uniformly. 
                #If a list of dicts is given, first a dict is sampled uniformly, 
                #and then a parameter is sampled using that dict as above.

                try:
                    rand_search = RandomizedSearchCV(
                        estimator = log_reg_base,
                        param_distributions = valid_params_list,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )
                    #random_state = 42 + window_start  # Corretto random_state


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_reshaped, y)

                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Controlla le combinazioni testate e conta quelle valide
                    #valid_combinations_count = 0

                    # Controlla le combinazioni testate
                    print(f"\n\033[1mValid hyperparameter combinations tested for n_window {window_start}-{window_end}\033[0m:\n")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:
                        for i, params in enumerate(rand_search.cv_results_['params']):
                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"Window {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n")

                        for params in rand_search.cv_results_['params']:
                            if valid_param_combination(params):
                                valid_combination_count += 1
                                print(f"\033[1mSolver\033[0m: {params['solver']}, \033[1mPenalty\033[0m: {params['penalty']}, \033[1mC\033[0m: {params['C']}", end = '')
                                if 'l1_ratio' in params:
                                    print(f", \033[1ml1_ratio\033[0m: {params['l1_ratio']}")
                                else:
                                    print()
                            else:
                                invalid_combination_count += 1
                                print(f"Invalid combination found: {params}")

                            #QUI

                        # Ottieni il modello con i migliori iper-parametri:

                        #Questa variabile ti restituisce il set di iper-parametri che ha prodotto il miglior punteggio 
                        #(migliore accuratezza) durante la Randomized Search per la finestra corrente. 
                        #È un dizionario che specifica valori come il solver, la penalizzazione, e altri iper-parametri.

                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                        #Questa variabile ti restituisce il punteggio (accuracy) del modello che ha ottenuto le migliori prestazioni 
                        #con i parametri in rand_search.best_params_. 
                        #Rappresenta la misura delle performance del modello sui dati di validazione durante la Randomized Search.

                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Stampa i risultati per la finestra corrente
                        #print(f"\033[1mWindow {window_start}-{window_end}\033[0m: Best Params = {best_model_params}, Best Score = {best_score}")

                    # Salva i parametri migliori per la finestra temporale corrente in una riga del file di testo
                    #with open(params_file_path, 'a') as f:
                    #    f.write(f"Window n° {time_point}\t{json.dumps(best_model_params)}\n")

                        # Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:
                    print(f"An error occurred for window {window_start}-{window_end}: {e}")
                    invalid_combination_count += 1

                    # Continua con l'iterazione successiva senza interrompere l'intero loop

                # Memorizza il tempo di fine per il punto temporale corrente
                time_point_end = time.time()

                # Calcola il tempo di esecuzione per il punto temporale corrente
                time_point_elapsed = time_point_end - time_point_start

                # Aggiungi il tempo di esecuzione alla lista
                execution_times.append(time_point_elapsed)

                # Stampa i risultati per il punto temporale corrente
                #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                print()
                print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds")
                print()


            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            print()
            print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                        f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                else:
                    f.write("No valid windows found in the specified range.\n")

                f.write('\n')
                f.write(f"Total execution time: {total_execution_time} seconds\n")
                f.write(f"Number of valid combinations: {valid_combination_count}\n")
                f.write(f"Number of invalid combinations: {invalid_combination_count}\n")

##### **ALL SINGLE Patients (PT01-PT15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

- **EEG preprocessed signal**: filtered 1-20


In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun soggetto nel dizionario
for soggetto, dati in new_subject_level_concatenations_pt_1_20.items():
    
    # Verifica che 'data' sia presente tra le chiavi
    if 'data' in dati:
        
        # Sotto-seleziona i canali di interesse
        dati_originali = dati['data']  # Estrai i dati
        
        dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali

        # Aggiorna la chiave 'data' con i dati filtrati
        new_subject_level_concatenations_pt_1_20[soggetto]['data'] = dati_sottoselezionati

        # Opzionale: stampa di controllo per verificare la nuova forma dei dati
        print(f"Soggetto {soggetto}: {dati_sottoselezionati.shape}")

In [ ]:
##### **ALL SINGLE Patients (PT01-PT15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DAL SEGNALE 1-20Hz**

import numpy as np
import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER MULTINOMIAL LOGISTIC REGRESSION'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra penalty e solver, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...


# Definizione dei parametri validi, ossia delle coppie solver-penalty associate
params = {'newton-cg': ['l2', None],
    'sag': ['l2', None],
    'saga': ['l1', 'l2', 'elasticnet', None],
    'lbfgs': ['l2', None]
}


# Assicuriamoci di non avere duplicati e di avere una lista di dizionari separati per solver e penalty
parameters_dist = {
    'solver': list(params.keys()),
    'penalty': list(set(penalty for penalties in params.values() for penalty in penalties)),
    'C': [0.001, 0.01, 0.1, 1, 10, 100]
    
}

print(f"\033[1mparameters_dist\033[0m è: {parameters_dist}")

def generate_valid_params(params):
    valid_params = []
    
    # Generate values from 0 to 1 (inclusive) with step 0.05
    l1_ratio_values = np.append(np.arange(0.0, 1.0, 0.05), 1.0)

    # Impongo parametro C con valori su scala logaritmica 
    C_values = [0.001, 0.01, 0.1, 1, 10, 100]

    for C in C_values: 
        for solver in params['solver']:
            if solver == 'newton-cg':
                penalties = ['l2', None]
            elif solver == 'sag':
                penalties = ['l2', None]
            elif solver == 'lbfgs':
                penalties = ['l2', None]
            elif solver == 'saga':
                penalties = ['l1', 'l2', 'elasticnet', None]  # Include None here explicitly
            else:
                penalties = params['penalty']
            
            # Create parameter dictionaries for each combination of solver and penalty
            for penalty in penalties:
                if penalty == 'elasticnet':
                    for l1_ratio in l1_ratio_values:
                        valid_params.append({'solver': [solver], 'penalty': ['elasticnet'], 'l1_ratio': [l1_ratio], 'C': [C]})
                        
                else:
                    valid_params.append({'solver': [solver], 'penalty': [penalty], 'C': [C]})
    
    return valid_params


# Funzione per verificare se una combinazione di iperparametri è valida
def valid_param_combination(params):
    solver = params['solver']
    penalty = params['penalty']
    
    if solver in ['newton-cg', 'lbfgs', 'sag'] and penalty in ['l2', None]:
        return True
    elif solver == 'saga' and penalty in ['l1', 'l2', 'elasticnet', None]:
        return True
    else:
        return False

valid_params_list = generate_valid_params(parameters_dist)
print(f"\n\033[1mvalid_params_list\033[0m è: {valid_params_list}")



# Itera attraverso i soggetti

#for subject, subj_dict in subject_level_concatenations_pt_1_20.items():
for subject, subj_dict in new_subject_level_concatenations_pt_1_20.items():
    
    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO'''
    
    #if subject == 'pt_16':
    #if subject == 'pt_17' or subject == 'pt_18' or subject == 'pt_19':
    #if subject == 'pt_20':

    print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")

    #print(f"\n\nCurrent Subject \033[1m{subject}\033[0m")

    print(f"\n\n\033[1mExtraction of Data\033[0m from Subject \033[1m{subject}\033[0m from Original Filtered Signal in \033[1m1-20Hz\033[0m")

    X = subj_dict['data'] # Estraiamo i dati del soggetto corrente

    y = subj_dict['labels'] # Estraiamo le labels livello corrente del soggetto corrente

    #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
    params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20'

    #FILE PATH DINAMICA PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
    #A SECONDA DEL SOGGETTO E LIVELLO DI RICOSTRUZIONE DEI DATI PRESI IN ESAME 

    # Costruzione del percorso del file in maniera dinamica
    params_file_path = f'{params_dir}/optimized_params_{subject}_filtered_1_20_std.txt'

    if not os.path.exists(params_dir):
        os.makedirs(params_dir)

    #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\t\033[1m{params_dir}\033[0m"),
    print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

    print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

    y = y.astype(int) 

    print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


    # Calcola il numero totale di etichette 
    label_counts = np.unique(y, return_counts = True)[1]
    total_labels = len(y)

    # Calcola la percentuale di ciascuna classe
    class_proportions = label_counts / total_labels * 100

    print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

    # Calcola i pesi delle classi come l'inverso delle proporzioni
    class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

    # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
    class_weights /= class_weights.sum()

    print(f"\n\033[1mClass Weights {class_weights}\033[0m")

    # Crea un dizionario per class_weight
    class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}

    '''INIZIALIZZAZIONE LOGISTIC REGRESSION'''

    # Inizializzo modello Logistic Regression base (da sklearn.LinearModel version 1.0.5)
    log_reg_base = LogisticRegression(class_weight = class_weight_dict, max_iter = 10000)

    # Memorizza il tempo di inizio
    start_time = time.time()

    # Lista per memorizzare i tempi di esecuzione per ogni istante temporale
    execution_times = []

    # Contatori per combinazioni valide e non valide
    valid_combination_count = 0
    invalid_combination_count = 0

    # File di output per i parametri ottimizzati
    with open(params_file_path, 'w') as f:
        f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")


    '''INIZIALIZZAZIONE RANDOM SEARCH'''

    # Inizializzazione della Random Search:

    #https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

    #cv: int, cross-validation generator or an iterable, default=None
    #Determines the cross-validation splitting strategy. 

    #Possible inputs for cv are:

    #None, to use the default 5-fold cross validation,
    #integer, to specify the number of folds in a (Stratified)KFold,
    #CV splitter,
    #An iterable yielding (train, test) splits as arrays of indices.

    #random_state: int, RandomState instance or None, default=None
    #Pseudo random number generator state used for random uniform sampling from lists of possible values 
    #instead of scipy.stats distributions. Pass an int for reproducible output across multiple function calls

    # RandomizedSearchCV è una tecnica di ricerca iperparametrica che 
    # campiona casualmente combinazioni di iperparametri da un insieme predefinito.

    #n_iter determina il numero di combinazioni di iperparametri da testare durante la ricerca


    # Lista per memorizzare i risultati delle finestre
    window_results = []

    # Creazione della finestra scorrevole con step e dimensioni desiderate
    n_samples = X.shape[2]
    window_size = 50
    step_size = 25
    n_windows = (n_samples - window_size) // step_size + 1


    ''' 
    50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 
    '''

    # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

    for window_start in range(0, n_samples - window_size + 1, step_size):

        # Memorizza il tempo di inizio per il punto temporale corrente
        time_point_start = time.time()

        # Definiamo la finestra corrente
        window_end = window_start + window_size

        X_window = X[:, :, window_start:window_end]
        print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

        # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
        X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
        print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

        # Standardizza i dati della finestra corrente
        scaler = StandardScaler()
        X_window_standardized = scaler.fit_transform(X_window_reshaped)
        print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

        #print(X_window_reshaped.shape)

        #Da https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

        #param_distributions: 

        #Dictionary with parameters names (str) as keys and distributions or lists of parameters to try. 
        #Distributions must provide a rvs method for sampling (such as those from scipy.stats.distributions). 
        #If a list is given, it is sampled uniformly. 
        #If a list of dicts is given, first a dict is sampled uniformly, 
        #and then a parameter is sampled using that dict as above.

        try:
            rand_search = RandomizedSearchCV(
                estimator = log_reg_base,
                param_distributions = valid_params_list,
                scoring ='accuracy',
                n_iter = 100,
                verbose = 1,
                n_jobs = -1
            )
            #random_state = 42 + window_start  # Corretto random_state

            '''
            50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 
            '''

            # Esegui RandomizedSearchCV sulla finestra corrente
            rand_search.fit(X_window_reshaped, y)

            # Controlla il numero totale di combinazioni testate
            total_combinations_tested = len(rand_search.cv_results_['params'])
            #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

            # Controlla le combinazioni testate e conta quelle valide
            #valid_combinations_count = 0

            # Controlla le combinazioni testate
            #print(f"\n\033[1mValid hyperparameter combinations tested for n_window {window_start}-{window_end}\033[0m:\n")

            # Salva tutte le combinazioni testate per la finestra corrente
            with open(params_file_path, 'a') as f:
                for i, params in enumerate(rand_search.cv_results_['params']):
                    score = rand_search.cv_results_['mean_test_score'][i]
                    f.write(f"Window {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n")

                for params in rand_search.cv_results_['params']:
                    if valid_param_combination(params):
                        valid_combination_count += 1
                        #print(f"\033[1mSolver\033[0m: {params['solver']}, \033[1mPenalty\033[0m: {params['penalty']}, \033[1mC\033[0m: {params['C']}", end = '')
                        #if 'l1_ratio' in params:
                        #    print(f", \033[1ml1_ratio\033[0m: {params['l1_ratio']}")
                        #else:
                            #print()
                    else:
                        invalid_combination_count += 1
                        print(f"Invalid combination found: {params}")

                    #QUI

                # Ottieni il modello con i migliori iper-parametri:

                #Questa variabile ti restituisce il set di iper-parametri che ha prodotto il miglior punteggio 
                #(migliore accuratezza) durante la Randomized Search per la finestra corrente. 
                #È un dizionario che specifica valori come il solver, la penalizzazione, e altri iper-parametri.

                best_model_params = rand_search.best_params_

                '''
                50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 
                '''

                #Questa variabile ti restituisce il punteggio (accuracy) del modello che ha ottenuto le migliori prestazioni 
                #con i parametri in rand_search.best_params_. 
                #Rappresenta la misura delle performance del modello sui dati di validazione durante la Randomized Search.

                best_score = rand_search.best_score_

                '''
                50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 
                '''
                # Memorizza i risultati della finestra corrente
                window_results.append({
                    'window_start': window_start,
                    'window_end': window_end,
                    'best_params': best_model_params,
                    'best_score': best_score
                })

                '''
                50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 
                '''
                # Stampa i risultati per la finestra corrente
                #print(f"\033[1mWindow {window_start}-{window_end}\033[0m: Best Params = {best_model_params}, Best Score = {best_score}")

            # Salva i parametri migliori per la finestra temporale corrente in una riga del file di testo
            #with open(params_file_path, 'a') as f:
            #    f.write(f"Window n° {time_point}\t{json.dumps(best_model_params)}\n")

                # Salva i parametri migliori per la finestra corrente in una riga del file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                f.write('\n')

        except Exception as e:
            print(f"An error occurred for window {window_start}-{window_end}: {e}")
            invalid_combination_count += 1

            # Continua con l'iterazione successiva senza interrompere l'intero loop

        # Memorizza il tempo di fine per il punto temporale corrente
        time_point_end = time.time()

        # Calcola il tempo di esecuzione per il punto temporale corrente
        time_point_elapsed = time_point_end - time_point_start

        # Aggiungi il tempo di esecuzione alla lista
        execution_times.append(time_point_elapsed)

        # Stampa i risultati per il punto temporale corrente
        #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
        #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
        #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
        #print()
        #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds")
        #print()


    # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

    # Definisci il range generale delle finestre che vuoi analizzare
    general_range = [0, 300]  # Puoi modificare il range se necessario

    # Filtra i risultati delle finestre nel range desiderato
    general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

    # Controlla se ci sono risultati validi all'interno del range specificato
    if general_results:

        # Trova la finestra con il punteggio migliore
        best_general_window = max(general_results, key=lambda x: x['best_score'])

        # Trova i parametri migliori per questa finestra specifica (se disponibili)
        best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
        best_general_window['best_params'] = best_params

        # Stampa le informazioni sulla finestra migliore trovata
        #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
        #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
        #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

    else:
        print("No valid windows found in the specified range.")


    # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
    window_results.append({
        'Best window_start': best_general_window['window_start'] if general_results else None,
        'Best window_end': best_general_window['window_end'] if general_results else None,
        'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
        'best_score': best_general_window['best_score'] if general_results else None
    })

    # Calcola il tempo di esecuzione totale
    end_time = time.time()
    total_execution_time = end_time - start_time

    #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
    #print()
    #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
    #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

    # Aggiungi il risultato della migliore finestra generale al file di testo
    with open(params_file_path, 'a') as f:
        f.write('\n')
        if general_results:
            best_general_window = max(general_results, key=lambda x: x['best_score'])
            f.write(f"BEST WINDOW OVERALL: "),
            f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
            f.write(f"\nBest Window End: {best_general_window['window_end']}"),
            f.write(f"\nBest Score: {best_general_window['best_score']}")

            if best_general_window['best_params'] is not None:
                f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
        else:
            f.write("No valid windows found in the specified range.\n")

        f.write('\n')
        f.write(f"Total execution time: {total_execution_time} seconds\n")
        f.write(f"Number of valid combinations: {valid_combination_count}\n")
        f.write(f"Number of invalid combinations: {invalid_combination_count}\n")

#### **ALL SINGLE Patients (PT01-PT20) for **COUPLED EXPERIMENTAL CONDITIONS****

#### Automatization of all steps from: 

1) "**new_subject_level_concatenations_coupled_exp_pt**" ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_coupled_exp_pt_1_20**": EEG preprocessed signal filtered 1-20Hz 

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''


#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
#    new_subject_level_concatenations_th = pickle.load(f)
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle
import numpy as np


with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt_1_20 = pickle.load(f)
    

    
#PER SALVARE I FILE
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('NOME DEL FILE.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations, f)


#subject_level_concatenations_th['th_1'].keys()

In [ ]:
print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_pt\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt['pt_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp'].keys()}")

In [ ]:
np.unique(new_subject_level_concatenations_coupled_exp_pt['pt_16']['theta']['baseline_vs_th_resp']['labels'],return_counts=True)

##### **Descrizione degli step nel codice per ottenere e salvare nelle paths le best score performances per il level 4 e 5 dalle ricostruzioni**:

Vorrei in questo caso, per velocizzare, iterare su 

subject_level_concatenations, che ha questa struttura...

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


al cui interno ha per ogni chiave di primo ordine, un altro dizionario annidato, che è fatto di queste chiavi


dict_keys(['theta', 'delta', 'labels'])

dentro 'theta' e 'delta' ci sono tutti i dati di tutte le condizioni sperimentali del singolo soggetto

del tipo 'theta' o 'delta' conterrà un array con shape

(204, 3, 300)

con 1° dimensione i trial, poi i canali, poi i punti di ogni trial (campioni EEG)

e dentro 'labels' ho invece l'array delle labels concatenate...
(204,)


<br>


Ora però, vorrei che ... 

Se ad esempio nel soggetto 'th_1' entri nella chiave 'theta', 

allora poi il file corrispondente .txt deve essere scritto con una path dinamica, che cambia a seconda 
- sia del soggetto iterato
- sia del livello di ricostruzione dei dati

Ossia:

la "params_dir" è fissa

mentre 

"params_file_path" è dinamica, e cambia a seconda del soggetto iterato e del livello. 

Per cui sarà una composizione di stringhe fisse e stringhe 'mobili', ossia

'params_file_path' = 'optimized_params_' + {subject} dove subject dovrebbe essere una lista di stringhe che si preleva dalle chiavi di primo ordine di "subject_level_concatenations" che erano

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


seguito da "_level_{level}_std" dove {level} dipende dal nome della chiave del sotto-dizionario iterato per ogni soggetto...

Ossia, ad esempio dentro il sotto-dizionario del primo soggetto di "subject_level_concatenations" cioè

subject_level_concatenations['th_1'], 

Se la sua sotto-chiave è 'theta' allora il level = 4, se la chiave è 'delta' allora il level = 5, 



Quindi la costruzione finale della path dinamica del file specifico per il soggetto 1 deve essere

 
params_file_path = 'optimized_params_' +'{subject}' + "_level_{level}_std.txt"

e sarà se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_1' + "_level_4_std.txt"


e sarà se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_1' + "_level_5_std.txt"


in questo modo, farei un loop unico su tutte le sottochiavi dei dizionari annidati dentro 
"subject_level_concatenations" 

ossia 
dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

e per ognuno vedo se la sua sotto-chiave sarà 'theta' o 'delta' e creerà dei file .txt corrispondenti nella param_dir che gli ho chiesto...

Il resto del codice non toccarlo invece, perché dovrebbe creare dei file .txt per ogni soggetto per ogni livello di ricostruzione dei dati,
e salverà le analisi nel file .txt corrispondente



Ad esempio, continuando col soggetto 2:

la costruzione finale della path dinamica del file specifico per il soggetto 2

Sarà, se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_2' + "_level_4_std.txt"


e sarà, se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_2' + "_level_5_std.txt"


e così via per tutti gli altri soggetti




##### **ALL SINGLE Patients (PT01-PT16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DALLE RICOSTRUZIONI** 

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**


###### **ISTRUZIONI PER MODIFICHE AL CASO 2 CLASSI**

Allora, andiamo per step:

**1)** la nuova variabile sulla quale iterare è new_subject_level_concatenations_coupled_exp_th

che è fatta con questa struttura

print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_th\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()}")

OUTPUT:

Dataset Organization: new_subject_level_concatenations_coupled_exp_th

First Order Key: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16'])

Second Order Key: dict_keys(['theta', 'delta', 'theta_strict'])

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

Fourth Order Key: dict_keys(['data', 'labels'])

quindi significa che, per ogni soggetto, tu dovrai entrare nella sotto sotto chiave relativa ai livelli di ricostruzione del segnale 

dict_keys(['theta', 'delta', 'theta_strict'])

per ognuna di queste, avrai appunto delle altre sotto-sotto-sotto chiavi, che sono le condizioni sperimentali, sulle quali dovrai entrare che sono 

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

dopodiché dentro ognuna di queste, dovrai entrare ulteriormente dentro ciascuna sotto chiave di quarto livello:

la prima, che fa riferimento ai dati('data') il cui valore (array numpy() verrà assegnato ad X nel codice, e 
la seconda, la chiave delle labels ('labels') il cui valore verrà assegnato ad Y...

**2)** questa parte relativa ai print

 for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'

voglio che poi abbia degli altri if, nel senso che vorrei che iterando su ogni livello, voglio che venga applicata la stessa logica dei printing di qui sopra, ma alle chiavi del 3° livello, ossia quelle che fanno riferimento alle condizioni sperimentali...

ossia, 

voglio che ci sia scritto per le X

print(f"\n\033[1mExtraction of Data\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

e voglio che ci sia scritto per le Y

print(f"\n\033[1mExtraction of Labels\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

dove 

"experimental_condition" farà riferimento alla chiave della condizione sperimentale iterata in quel loop, e 

"level_key" invece farà riferimento alle chiavi del 2° livello, ossia a quelle che si riferiscono allo specifico livello di ricostruzione del segnale per il quale io sto estraendo i dati e le labels al ciclo corrente...

In questo modo, dovrei avere un'idea dai print del mio codice, quando viene eseguito, su quale soggetto, quale livello e quale condizione sperimentale sta eseguendo i calcoli.. 

**3)** voglio che vengano create dei folder nuovi per appendere i risultati di tutte le elaborazioni da parte dei vari modelli e che saranno queste due cartelle

"EEG_50_window_25_overlap_coupled_exp_cond" 
"single_therapist_optimized_params_coupled_exp_cond"
 
ossia la mia directory dovrebbe diventare

params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond'

per cui, se "EEG_50_window_25_overlap_coupled_exp_cond" né "single_therapist_optimized_params_coupled_exp_cond" non sono state create, allora andranno create...

**4)** la creazione del nome del file relativo ad un determinato soggetto dovrà essere formato in questo modo

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

dove, ricorda, "experimental_condition" farà riferimento alle insieme delle stringhe che compongono la chiave della condizione sperimentale iterata in quel loop (chiavi di 3° livello di "new_subject_level_concatenations_coupled_exp_th" 

del tipo potrebbe essere

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

Con ad esempio:

subject = th_1
level = theta 
experimental_condition = baseline_vs_th_resp

per cui sarebbe 

f'{params_dir}/optimized_params_th_1_level_theta_baseline_vs_th_resp_std.txt'

**5)** al momento, il settaggio degli iper-parametri è impostato per anche per i casi multi-nomiali ma in questo caso il codice verrà usato per task di classificazione binaria...

per cui, voglio essere sicuro che l'impostazione attuale vada anche bene per i casi semplicemente binomiali, ossia di due possibili classi solo...

per farlo, ti do il link della pagina della Logistic Regression, in modo che tu mi dica se l'attuale implementazione sia corretta....

https://scikit-learn.org/1.5/modules/generated/sklearn.linear_model.LogisticRegression.html


**6)** Fai le modifiche a quello che ti ho chiesto, non azzardare cose in più od in meno, vorrei che ti attenessi a ciò che ti ho chiesto...


##### **IMPLEMENTATION LOGISTIC REGRESSION FOR COUPLED EXPERIMENTAL CONDITIONS**

In [ ]:
new_subject_level_concatenations_coupled_exp_pt['pt_7']['theta']['baseline_vs_th_resp'].keys()

In [ ]:
''' PATIENTS!

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ, Θ, δ e Θ strict!)


******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* *******
#DIRECTORY PATH MESSA INIZIALMENTE  

# -->>>>> /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/prova/ <<<<<--

#PER NON SOVRASCRIVERE RISULTATI RANDOM SEARCH SU TUTTI I SOGGETTI CON LOGISTIC REGRESSION!!!!!

******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* ******* *******


Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare

#Some penalties may not work with some solvers. 
#See the parameter solver below, to know the compatibility between the penalty and solver.


Per la classificazione multi-classe con l'opzione multi_class='multinomial', 
puoi utilizzare i seguenti solver e le relative penalità:

newton-cg: supporta solo l2 e None.
sag: supporta solo l2 e None.
saga: supporta l1, l2, elasticnet, e None.
lbfgs: supporta solo l2 e None.

Quindi, se vuoi esplorare solo il caso multinomiale, puoi utilizzare i seguenti abbinamenti di solver e penalità:

newton-cg: l2, None
sag: l2, None
saga: l1, l2, elasticnet, None
lbfgs: l2, None

'''

import numpy as np
import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

import torch

'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER MULTINOMIAL LOGISTIC REGRESSION'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra penalty e solver, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...


# Definizione dei parametri validi, ossia delle coppie solver-penalty associate
params = {'newton-cg': ['l2', None],
    'sag': ['l2', None],
    'saga': ['l1', 'l2', 'elasticnet', None],
    'lbfgs': ['l2', None]
}


# Assicuriamoci di non avere duplicati e di avere una lista di dizionari separati per solver e penalty
parameters_dist = {
    'solver': list(params.keys()),
    'penalty': list(set(penalty for penalties in params.values() for penalty in penalties)),
    'C': [0.001, 0.01, 0.1, 1, 10, 100]
    
}

print(f"\033[1mparameters_dist\033[0m è: {parameters_dist}")

def generate_valid_params(params):
    valid_params = []
    
    # Generate values from 0 to 1 (inclusive) with step 0.05
    l1_ratio_values = np.append(np.arange(0.0, 1.0, 0.05), 1.0)

    # Impongo parametro C con valori su scala logaritmica 
    C_values = [0.001, 0.01, 0.1, 1, 10, 100]

    for C in C_values: 
        for solver in params['solver']:
            if solver == 'newton-cg':
                penalties = ['l2', None]
            elif solver == 'sag':
                penalties = ['l2', None]
            elif solver == 'lbfgs':
                penalties = ['l2', None]
            elif solver == 'saga':
                penalties = ['l1', 'l2', 'elasticnet', None]  # Include None here explicitly
            else:
                penalties = params['penalty']
            
            # Create parameter dictionaries for each combination of solver and penalty
            for penalty in penalties:
                if penalty == 'elasticnet':
                    for l1_ratio in l1_ratio_values:
                        valid_params.append({'solver': [solver], 'penalty': ['elasticnet'], 'l1_ratio': [l1_ratio], 'C': [C]})
                        
                else:
                    valid_params.append({'solver': [solver], 'penalty': [penalty], 'C': [C]})
    
    return valid_params


# Funzione per verificare se una combinazione di iperparametri è valida
def valid_param_combination(params):
    solver = params['solver']
    penalty = params['penalty']
    
    if solver in ['newton-cg', 'lbfgs', 'sag'] and penalty in ['l2', None]:
        return True
    elif solver == 'saga' and penalty in ['l1', 'l2', 'elasticnet', None]:
        return True
    else:
        return False

valid_params_list = generate_valid_params(parameters_dist)
print(f"\n\033[1mvalid_params_list\033[0m è: {valid_params_list}")




# Itera attraverso i soggetti

'''OLD VERSION'''
#for subject, levels in subject_level_concatenations.items():

'''NEW VERSION'''
#for subject, levels in new_subject_level_concatenations_th.items():


'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_patient_optimized_params_coupled_exp_cond"

# Iterazione sulla struttura `new_subject_level_concatenations_coupled_exp_pt`

for subject, levels in new_subject_level_concatenations_coupled_exp_pt.items():
    
    
    if subject == 'pt_1' or subject == 'pt_7':
        
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")

        for level_key, experimental_condition in levels.items():

            # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
            #                                      'delta' = δ,i.e., approx_5 ,
            #                                      'theta_strict' = Θ, i.e., detail_5,
            #                                      'labels') 

            # Identificazione del livello
            if level_key == 'theta':
                level = "approx_4"


            elif level_key == 'delta':
                level = "approx_5"


            elif level_key == 'theta_strict':
                level = "detail_5"

            else:
                continue  # Ignora livelli non rilevanti


            print(f"\nProcessing Data \033[1m from Level: \033[1m{level_key}\033[0m for Subject \033[1m{subject}\033[0m")

            for condition, data_dict in experimental_condition.items():

                if condition == "baseline_vs_th_resp":

                    # Estrazione dei dati e delle label
                    X = data_dict['data'] # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente

                    # Messaggi di log per dati e label
                    print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

                    print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

                    y = data_dict['labels'] # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente


                    '''NEW VERSION'''
                    #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
                    params_dir = params_dir

                    # Creazione della cartella, se non esiste
                    if not os.path.exists(params_dir):
                        os.makedirs(params_dir)
                        print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


                    # Costruzione del percorso del file in maniera dinamica
                    params_file_path = f"{params_dir}/optimized_params_{subject}_level_{level}_{condition}_std.txt"

                    print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")
                    print(f"\033[1m{params_file_path}\033[0m\n")

                    print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

                    y = y.astype(int) 

                    print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


                    # Calcola il numero totale di etichette livello 4/5°
                    label_counts = np.unique(y, return_counts = True)[1]
                    total_labels = len(y)

                    # Calcola la percentuale di ciascuna classe
                    class_proportions = label_counts / total_labels * 100

                    print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

                    # Calcola i pesi delle classi come l'inverso delle proporzioni
                    class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

                    # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
                    class_weights /= class_weights.sum()

                    print(f"\n\033[1mClass Weights {class_weights}\033[0m")

                    # Crea un dizionario per class_weight
                    class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


                    #INIZIALIZZAZIONE LOGISTIC REGRESSION

                # Inizializzo modello Logistic Regression base (da sklearn.LinearModel version 1.0.5)
                log_reg_base = LogisticRegression(class_weight = class_weight_dict, max_iter = 20000)

                # Memorizza il tempo di inizio
                start_time = time.time()

                # Lista per memorizzare i tempi di esecuzione per ogni istante temporale
                execution_times = []

                # Contatori per combinazioni valide e non valide
                valid_combination_count = 0
                invalid_combination_count = 0


                # File di output per i parametri ottimizzati
                with open(params_file_path, 'w') as f:
                    f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

                    #INIZIALIZZAZIONE RANDOM SEARCH

                    # Inizializzazione della Random Search:

                    #https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

                    #cv: int, cross-validation generator or an iterable, default=None
                    #Determines the cross-validation splitting strategy. 

                    #Possible inputs for cv are:

                    #None, to use the default 5-fold cross validation,
                    #integer, to specify the number of folds in a (Stratified)KFold,
                    #CV splitter,
                    #An iterable yielding (train, test) splits as arrays of indices.

                    #random_state: int, RandomState instance or None, default=None
                    #Pseudo random number generator state used for random uniform sampling from lists of possible values 
                    #instead of scipy.stats distributions. Pass an int for reproducible output across multiple function calls

                    # RandomizedSearchCV è una tecnica di ricerca iperparametrica che 
                    # campiona casualmente combinazioni di iperparametri da un insieme predefinito.

                    #n_iter determina il numero di combinazioni di iperparametri da testare durante la ricerca


                    # Lista per memorizzare i risultati delle finestre
                    window_results = []

                    # Creazione della finestra scorrevole con step e dimensioni desiderate
                    n_samples = X.shape[2]
                    window_size = 50
                    step_size = 25
                    n_windows = (n_samples - window_size) // step_size + 1


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                    # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente
                    for window_start in range(0, n_samples - window_size + 1, step_size):

                        # Memorizza il tempo di inizio per il punto temporale corrente
                        time_point_start = time.time()

                        # Definiamo la finestra corrente
                        window_end = window_start + window_size

                        X_window = X[:, :, window_start:window_end]
                        print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                        # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                        X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                        print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                        # Standardizza i dati della finestra corrente
                        scaler = StandardScaler()
                        X_window_standardized = scaler.fit_transform(X_window_reshaped)
                        print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                        #print(X_window_reshaped.shape)

                        #Da https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

                        #param_distributions: 

                        #Dictionary with parameters names (str) as keys and distributions or lists of parameters to try. 
                        #Distributions must provide a rvs method for sampling (such as those from scipy.stats.distributions). 
                        #If a list is given, it is sampled uniformly. 
                        #If a list of dicts is given, first a dict is sampled uniformly, 
                        #and then a parameter is sampled using that dict as above.

                        try:
                            rand_search = RandomizedSearchCV(
                                estimator = log_reg_base,
                                param_distributions = valid_params_list,
                                scoring ='accuracy',
                                n_iter = 100,
                                verbose = 1,
                                n_jobs = -1
                            )
                            #random_state = 42 + window_start  # Corretto random_state


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                            # Esegui RandomizedSearchCV sulla finestra corrente
                            rand_search.fit(X_window_reshaped, y)

                            # Controlla il numero totale di combinazioni testate
                            total_combinations_tested = len(rand_search.cv_results_['params'])
                            #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                            # Controlla le combinazioni testate e conta quelle valide
                            #valid_combinations_count = 0

                            # Controlla le combinazioni testate
                            #print(f"\n\033[1mValid hyperparameter combinations tested for n_window {window_start}-{window_end}\033[0m:\n")

                            # Salva tutte le combinazioni testate per la finestra corrente
                            with open(params_file_path, 'a') as f:
                                for i, params in enumerate(rand_search.cv_results_['params']):
                                    score = rand_search.cv_results_['mean_test_score'][i]
                                    f.write(f"Window {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n")

                                for params in rand_search.cv_results_['params']:
                                    if valid_param_combination(params):
                                        valid_combination_count += 1
                                        #print(f"\033[1mSolver\033[0m: {params['solver']}, \033[1mPenalty\033[0m: {params['penalty']}, \033[1mC\033[0m: {params['C']}", end = '')
                                        #if 'l1_ratio' in params:
                                        #    print(f", \033[1ml1_ratio\033[0m: {params['l1_ratio']}")
                                        #else:
                                        #    print()
                                    else:
                                        invalid_combination_count += 1
                                        #print(f"Invalid combination found: {params}")

                                    #QUI

                                # Ottieni il modello con i migliori iper-parametri:

                                #Questa variabile ti restituisce il set di iper-parametri che ha prodotto il miglior punteggio 
                                #(migliore accuratezza) durante la Randomized Search per la finestra corrente. 
                                #È un dizionario che specifica valori come il solver, la penalizzazione, e altri iper-parametri.

                                best_model_params = rand_search.best_params_


                                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                                #Questa variabile ti restituisce il punteggio (accuracy) del modello che ha ottenuto le migliori prestazioni 
                                #con i parametri in rand_search.best_params_. 
                                #Rappresenta la misura delle performance del modello sui dati di validazione durante la Randomized Search.

                                best_score = rand_search.best_score_


                                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                                # Memorizza i risultati della finestra corrente
                                window_results.append({
                                    'window_start': window_start,
                                    'window_end': window_end,
                                    'best_params': best_model_params,
                                    'best_score': best_score
                                })


                                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                                # Stampa i risultati per la finestra corrente
                                #print(f"\033[1mWindow {window_start}-{window_end}\033[0m: Best Params = {best_model_params}, Best Score = {best_score}")

                            # Salva i parametri migliori per la finestra temporale corrente in una riga del file di testo
                            #with open(params_file_path, 'a') as f:
                            #    f.write(f"Window n° {time_point}\t{json.dumps(best_model_params)}\n")

                                # Salva i parametri migliori per la finestra corrente in una riga del file di testo
                            with open(params_file_path, 'a') as f:
                                f.write('\n')
                                f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                                f.write('\n')

                        except Exception as e:
                            print(f"An error occurred for window {window_start}-{window_end}: {e}")
                            invalid_combination_count += 1

                            # Continua con l'iterazione successiva senza interrompere l'intero loop

                        # Memorizza il tempo di fine per il punto temporale corrente
                        time_point_end = time.time()

                        # Calcola il tempo di esecuzione per il punto temporale corrente
                        time_point_elapsed = time_point_end - time_point_start

                        # Aggiungi il tempo di esecuzione alla lista
                        execution_times.append(time_point_elapsed)

                        # Stampa i risultati per il punto temporale corrente
                        #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                        #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                        #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                        #print()
                        #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds")
                        #print()


                    # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

                    # Definisci il range generale delle finestre che vuoi analizzare
                    general_range = [0, 300]  # Puoi modificare il range se necessario

                    # Filtra i risultati delle finestre nel range desiderato
                    general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

                    # Controlla se ci sono risultati validi all'interno del range specificato
                    if general_results:

                        # Trova la finestra con il punteggio migliore
                        best_general_window = max(general_results, key=lambda x: x['best_score'])

                        # Trova i parametri migliori per questa finestra specifica (se disponibili)
                        best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                        best_general_window['best_params'] = best_params

                        # Stampa le informazioni sulla finestra migliore trovata
                        #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                        #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                        #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

                    else:
                        print("No valid windows found in the specified range.")


                    # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
                    window_results.append({
                        'Best window_start': best_general_window['window_start'] if general_results else None,
                        'Best window_end': best_general_window['window_end'] if general_results else None,
                        'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                        'best_score': best_general_window['best_score'] if general_results else None
                    })

                    # Calcola il tempo di esecuzione totale
                    end_time = time.time()
                    total_execution_time = end_time - start_time

                    #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
                    #print()
                    #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
                    #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

                    # Aggiungi il risultato della migliore finestra generale al file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        if general_results:
                            best_general_window = max(general_results, key=lambda x: x['best_score'])
                            f.write(f"BEST WINDOW OVERALL: "),
                            f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                            f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                            f.write(f"\nBest Score: {best_general_window['best_score']}")

                            if best_general_window['best_params'] is not None:
                                f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                        else:
                            f.write("No valid windows found in the specified range.\n")

                        f.write('\n')
                        f.write(f"Total execution time: {total_execution_time} seconds\n")
                        f.write(f"Number of valid combinations: {valid_combination_count}\n")
                        f.write(f"Number of invalid combinations: {invalid_combination_count}\n")


##### **ALL SINGLE Patients (PT01-PT16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **EEG preprocessed signal**: filtered 1-20

In [ ]:
#new_subject_level_concatenations_pt_1_20.keys()
#new_subject_level_concatenations_pt_1_20['pt_1'].keys()

#new_subject_level_concatenations_coupled_exp_pt.keys()

#new_subject_level_concatenations_coupled_exp_pt_1_20.keys()
#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1'].keys()


#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp'].keys()

In [ ]:
import pickle
import numpy as np


with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt_1_20 = pickle.load(f)

In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun livello temporale (th_1, th_2, ..., th_16)
for id_subj in new_subject_level_concatenations_coupled_exp_pt_1_20.keys():
    
    # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
    for exp_cond in new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj].keys():
        
        # Verifica che 'data' sia presente tra le chiavi della condizione
        if 'data' in new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj][exp_cond]:
            
            # Estrai i dati originali
            dati_originali = new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj][exp_cond]['data']
            
            # Sotto-seleziona i canali di interesse
            dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali
            
            # Aggiorna la chiave 'data' con i dati filtrati
            new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj][exp_cond]['data'] = dati_sottoselezionati

            # Opzionale: stampa di controllo per verificare la nuova forma dei dati
            print(f"Subj \033[1m{id_subj}\033[0m, Condizione \033[1m{exp_cond}\033[0m: {dati_sottoselezionati.shape}")

In [ ]:
new_subject_level_concatenations_coupled_exp_pt_1_20.keys()
np.shape(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp']['data'])

In [ ]:
##### **ALL SINGLE Therapists (TH01-TH16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DAL SEGNALE 1-20Hz**

import numpy as np
import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER MULTINOMIAL LOGISTIC REGRESSION'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra penalty e solver, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...


# Definizione dei parametri validi, ossia delle coppie solver-penalty associate
params = {'newton-cg': ['l2', None],
    'sag': ['l2', None],
    'saga': ['l1', 'l2', 'elasticnet', None],
    'lbfgs': ['l2', None]
}


# Assicuriamoci di non avere duplicati e di avere una lista di dizionari separati per solver e penalty
parameters_dist = {
    'solver': list(params.keys()),
    'penalty': list(set(penalty for penalties in params.values() for penalty in penalties)),
    'C': [0.001, 0.01, 0.1, 1, 10, 100]
    
}

print(f"\033[1mparameters_dist\033[0m è: {parameters_dist}")

def generate_valid_params(params):
    valid_params = []
    
    # Generate values from 0 to 1 (inclusive) with step 0.05
    l1_ratio_values = np.append(np.arange(0.0, 1.0, 0.05), 1.0)

    # Impongo parametro C con valori su scala logaritmica 
    C_values = [0.001, 0.01, 0.1, 1, 10, 100]

    for C in C_values: 
        for solver in params['solver']:
            if solver == 'newton-cg':
                penalties = ['l2', None]
            elif solver == 'sag':
                penalties = ['l2', None]
            elif solver == 'lbfgs':
                penalties = ['l2', None]
            elif solver == 'saga':
                penalties = ['l1', 'l2', 'elasticnet', None]  # Include None here explicitly
            else:
                penalties = params['penalty']
            
            # Create parameter dictionaries for each combination of solver and penalty
            for penalty in penalties:
                if penalty == 'elasticnet':
                    for l1_ratio in l1_ratio_values:
                        valid_params.append({'solver': [solver], 'penalty': ['elasticnet'], 'l1_ratio': [l1_ratio], 'C': [C]})
                        
                else:
                    valid_params.append({'solver': [solver], 'penalty': [penalty], 'C': [C]})
    
    return valid_params


# Funzione per verificare se una combinazione di iperparametri è valida
def valid_param_combination(params):
    solver = params['solver']
    penalty = params['penalty']
    
    if solver in ['newton-cg', 'lbfgs', 'sag'] and penalty in ['l2', None]:
        return True
    elif solver == 'saga' and penalty in ['l1', 'l2', 'elasticnet', None]:
        return True
    else:
        return False

valid_params_list = generate_valid_params(parameters_dist)
print(f"\n\033[1mvalid_params_list\033[0m è: {valid_params_list}")


'''
# Itera su ciascun livello temporale (th_1, th_2, ..., th_16)
for id_subj in new_subject_level_concatenations_coupled_exp_th_1_20.keys():
    
    # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
    for exp_cond in new_subject_level_concatenations_coupled_exp_th_1_20[id_subj].keys():
        
        # Verifica che 'data' sia presente tra le chiavi della condizione
        if 'data' in new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]:
            
            # Estrai i dati originali
            dati_originali = new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]['data']
            
            # Sotto-seleziona i canali di interesse
            dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali
            
            # Aggiorna la chiave 'data' con i dati filtrati
            new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]['data'] = dati_sottoselezionati

            # Opzionale: stampa di controllo per verificare la nuova forma dei dati
            print(f"Subj \033[1m{id_subj}\033[0m, Condizione \033[1m{exp_cond}\033[0m: {dati_sottoselezionati.shape}")
'''
'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_patient_optimized_params_coupled_exp_cond_1_20"

for idx_subj, subject_data in new_subject_level_concatenations_coupled_exp_pt_1_20.items():
    
    level_str = 'filtered_1_20'
    
    #if id_subj == 'th_1':
    
    #if idx_subj == 'pt_17' or idx_subj == 'pt_18' or idx_subj == 'pt_19':
    
    if idx_subj == 'pt_20':
        
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {idx_subj}\033[0m\n\n")

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        #for condition in new_subject_level_concatenations_coupled_exp_th_1_20[idx_subj].keys():

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        for condition, condition_data in subject_data.items():

            #print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Creazione stringa per salvataggio files ('filtered_1_20')
            #level_str == 'filtered_1_20'

            print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente
            #X = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['data']

            # Estrazione dei dati e delle etichette
            X = condition_data['data']


            # Messaggi di log per dati e label
            print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente
            #y = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['labels'] 

            y = condition_data['labels']

            print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            '''NEW VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            params_dir = params_dir

            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f"{params_dir}/optimized_params_{idx_subj}_level_{level_str}_{condition}_std.txt"

            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{idx_subj}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")

            print(f"\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE LOGISTIC REGRESSION

            # Inizializzo modello Logistic Regression base (da sklearn.LinearModel version 1.0.5)
            log_reg_base = LogisticRegression(class_weight = class_weight_dict, max_iter = 20000)

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni istante temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0


            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")


                ##INIZIALIZZAZIONE RANDOM SEARCH

                # Inizializzazione della Random Search:

                #https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

                #cv: int, cross-validation generator or an iterable, default=None
                #Determines the cross-validation splitting strategy. 

                #Possible inputs for cv are:

                #None, to use the default 5-fold cross validation,
                #integer, to specify the number of folds in a (Stratified)KFold,
                #CV splitter,
                #An iterable yielding (train, test) splits as arrays of indices.

                #random_state: int, RandomState instance or None, default=None
                #Pseudo random number generator state used for random uniform sampling from lists of possible values 
                #instead of scipy.stats distributions. Pass an int for reproducible output across multiple function calls

                # RandomizedSearchCV è una tecnica di ricerca iperparametrica che 
                # campiona casualmente combinazioni di iperparametri da un insieme predefinito.

                #n_iter determina il numero di combinazioni di iperparametri da testare durante la ricerca


                # Lista per memorizzare i risultati delle finestre
                window_results = []

                # Creazione della finestra scorrevole con step e dimensioni desiderate
                n_samples = X.shape[2]
                window_size = 50
                step_size = 25
                n_windows = (n_samples - window_size) // step_size + 1


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente
                for window_start in range(0, n_samples - window_size + 1, step_size):

                    # Memorizza il tempo di inizio per il punto temporale corrente
                    time_point_start = time.time()

                    # Definiamo la finestra corrente
                    window_end = window_start + window_size

                    X_window = X[:, :, window_start:window_end]
                    print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                    # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                    X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                    print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                    # Standardizza i dati della finestra corrente
                    scaler = StandardScaler()
                    X_window_standardized = scaler.fit_transform(X_window_reshaped)
                    print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                    #print(X_window_reshaped.shape)

                    #Da https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

                    #param_distributions: 

                    #Dictionary with parameters names (str) as keys and distributions or lists of parameters to try. 
                    #Distributions must provide a rvs method for sampling (such as those from scipy.stats.distributions). 
                    #If a list is given, it is sampled uniformly. 
                    #If a list of dicts is given, first a dict is sampled uniformly, 
                    #and then a parameter is sampled using that dict as above.

                    try:
                        rand_search = RandomizedSearchCV(
                            estimator = log_reg_base,
                            param_distributions = valid_params_list,
                            scoring ='accuracy',
                            n_iter = 100,
                            verbose = 1,
                            n_jobs = -1
                        )
                        #random_state = 42 + window_start  # Corretto random_state


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Esegui RandomizedSearchCV sulla finestra corrente
                        rand_search.fit(X_window_reshaped, y)

                        # Controlla il numero totale di combinazioni testate
                        total_combinations_tested = len(rand_search.cv_results_['params'])
                        #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                        # Controlla le combinazioni testate e conta quelle valide
                        #valid_combinations_count = 0

                        # Controlla le combinazioni testate
                        #print(f"\n\033[1mValid hyperparameter combinations tested for n_window {window_start}-{window_end}\033[0m:\n")

                        # Salva tutte le combinazioni testate per la finestra corrente
                        with open(params_file_path, 'a') as f:
                            for i, params in enumerate(rand_search.cv_results_['params']):
                                score = rand_search.cv_results_['mean_test_score'][i]
                                f.write(f"Window {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n")

                            for params in rand_search.cv_results_['params']:
                                if valid_param_combination(params):
                                    valid_combination_count += 1
                                    #print(f"\033[1mSolver\033[0m: {params['solver']}, \033[1mPenalty\033[0m: {params['penalty']}, \033[1mC\033[0m: {params['C']}", end = '')
                                    #if 'l1_ratio' in params:
                                    #    print(f", \033[1ml1_ratio\033[0m: {params['l1_ratio']}")
                                    #else:
                                    #    print()
                                else:
                                    invalid_combination_count += 1
                                    #print(f"Invalid combination found: {params}")

                                #QUI

                            # Ottieni il modello con i migliori iper-parametri:

                            #Questa variabile ti restituisce il set di iper-parametri che ha prodotto il miglior punteggio 
                            #(migliore accuratezza) durante la Randomized Search per la finestra corrente. 
                            #È un dizionario che specifica valori come il solver, la penalizzazione, e altri iper-parametri.

                            best_model_params = rand_search.best_params_


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 


                            #Questa variabile ti restituisce il punteggio (accuracy) del modello che ha ottenuto le migliori prestazioni 
                            #con i parametri in rand_search.best_params_. 
                            #Rappresenta la misura delle performance del modello sui dati di validazione durante la Randomized Search.

                            best_score = rand_search.best_score_


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                            # Memorizza i risultati della finestra corrente
                            window_results.append({
                                'window_start': window_start,
                                'window_end': window_end,
                                'best_params': best_model_params,
                                'best_score': best_score
                            })


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                            # Stampa i risultati per la finestra corrente
                            #print(f"\033[1mWindow {window_start}-{window_end}\033[0m: Best Params = {best_model_params}, Best Score = {best_score}")

                        # Salva i parametri migliori per la finestra temporale corrente in una riga del file di testo
                        #with open(params_file_path, 'a') as f:
                        #    f.write(f"Window n° {time_point}\t{json.dumps(best_model_params)}\n")

                            # Salva i parametri migliori per la finestra corrente in una riga del file di testo
                        with open(params_file_path, 'a') as f:
                            f.write('\n')
                            f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                            f.write('\n')

                    except Exception as e:
                        print(f"An error occurred for window {window_start}-{window_end}: {e}")
                        invalid_combination_count += 1

                        # Continua con l'iterazione successiva senza interrompere l'intero loop

                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds")
                    #print()


                # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

                # Definisci il range generale delle finestre che vuoi analizzare
                general_range = [0, 300]  # Puoi modificare il range se necessario

                # Filtra i risultati delle finestre nel range desiderato
                general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

                # Controlla se ci sono risultati validi all'interno del range specificato
                if general_results:

                    # Trova la finestra con il punteggio migliore
                    best_general_window = max(general_results, key=lambda x: x['best_score'])

                    # Trova i parametri migliori per questa finestra specifica (se disponibili)
                    best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                    best_general_window['best_params'] = best_params

                    # Stampa le informazioni sulla finestra migliore trovata
                    #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                    #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                    #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

                else:
                    print("No valid windows found in the specified range.")


                # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
                window_results.append({
                    'Best window_start': best_general_window['window_start'] if general_results else None,
                    'Best window_end': best_general_window['window_end'] if general_results else None,
                    'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                    'best_score': best_general_window['best_score'] if general_results else None
                })

                # Calcola il tempo di esecuzione totale
                end_time = time.time()
                total_execution_time = end_time - start_time

                #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
                #print()
                #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
                #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

                # Aggiungi il risultato della migliore finestra generale al file di testo
                with open(params_file_path, 'a') as f:
                    f.write('\n')
                    if general_results:
                        best_general_window = max(general_results, key=lambda x: x['best_score'])
                        f.write(f"BEST WINDOW OVERALL: "),
                        f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                        f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                        f.write(f"\nBest Score: {best_general_window['best_score']}")

                        if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n")



#### **ALL SINGLE Patients (PT01-TH20)**

#### **PLOTS of EACH SINGLE Subject's Accuracy Score Performances** 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ and δ)**

<br>

#### Apri cella qui sotto per **istruzione da fornire per il codice**

##### **Descrizione degli step nel codice per estrarre dalle paths le best score performances salvate per il level 4 e 5 dalle ricostruzioni**:

Fammi un codice python che faccia queste cose 

- **1)** Entrami in una **folder path** (che ti fornisco io) ed iteri in quella folder path
- **2)** Vedi se c'è in quella folder path ci siano dei **file che finiscono con .txt**: 

- **3)** Se vedi la porzione finale del file contiene la stringa 
    **"all_th_level_4_std"** o 
    **all_th_level_5_std"**

   e se incontri queste stringhe, **escludi quei file .txt** e continua.. 

- **4)** Vedi invece se la porzione finale del file contiene la stringa **"_level_4_std"** o **"_level_5_std**:

- - **4.1.)** In quel caso, entri dentro quel file e **leggilo** ma poi fai una ulteriore considerazione, ossia
  - - vedi se quello che precede "_level_4_std" o "_level_5_std" sia **" th_"** dove * è un **suffisso dinamico**, che va da
      1 a 15...

Quindi avrai per ogni soggetto, due file .txt, che finiranno con questa stringa 

Per il **soggetto 1**: "**pt_1_level_4_std**" o "**pt_1_level_5_std**" 
Per il **soggetto 2**: "**pt_2_level_4_std**" o "**pt_2_level_5_std**" 

E così via, fino al 15° soggetto...

- **5)** Vedi in ognuna delle coppie di file .txt dello stesso soggetto
 
(i.e., ossia per esempio avrai per il soggetto 1 due file .txt, che finiranno con questa stringa 

"pt_1_level_4_std" o "pt_1_level_5_std" )

- **7)** Leggi il file .txt e vedi se ci sia un **riga in quel file .txt** con scritto 

**"Best Score for Window"**, seguito da **una sequenza di stringhe dinamica**, che cambia e che può essere presa da una lista di stringhe iterativamente che si costruisce a priori, del tipo:

"0-50" "25-75" etc., ossia che cambia di 25 valori ogni volta in maniera uniforme, quindi proseguendo sarebbe:
"50-100" "75-125" "100-150" "125-175" "150-200" "175-225" "200-250" "225-275" "250-300"

Quindi la lista di stringa dinamica potrebbe essere

**n_windows** = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"]

di conseguenza, itera per ogni elemento di questa lista "n_windows" per riconoscere se questa **sequenza di stringa dinamica** completi un riga dentro il file .txt che avrà scritto quindi:
 
**"Best Score for Window" + {elemento della lista "n_windows}**:"

A questo punto, avrai l'intera riga che sarà ad esempio:

"Best Score for Window 0-50: ".. 

In quella stessa riga del file .txt, dovresti trovare un **valore float**.. 

- **8)** Vorrei che prendessi quel valore float e **lo appendessi ad un dizionario**, che conterrà nei suoi vari valori i vari **best score ottenuti da quel soggetto lì, per ciascuna delle finestra considerate**
(che vanno da 0-50 a 250-300, ossia prendendo a riferimento quello che c'è dentro "n_windows"

'n_windows = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"])

Questo dizionario la chiamerò ad esempio **"best_scores_level_4_single_pt"**, che ad esempio avrà, 

come primo "valore", la chiave associata al primo soggetto (i.e, **pt_1**)

il quale poi avrà 

- - **A)** come sotto-chiave il nome dell'elemento iterato rispetto a "n_windows" e 
- - **B)** come sotto-valore il valore float associato al best score trovato per quella finestra lì, per quel soggetto lì, del tipo

**pt_1** =  {'**0-50**': valore float del best score ottenuto dal soggetto 1 sulla finestra 0-50,  
'25-75': valore float del best score ottenuto dal soggetto 1 sulla finestra 25-75... etc] 

quindi in sostanza, "**best_scores_level_4_single_pt**" sarà un **dizionario annidato**, 

che conterrà altri dizionari, ognuno con il nome del soggetto e 
come sotto-chiave del sottodizionario il valore stringa di quella finestra, 
come sotto-valore, il valore di best score ottenuto da quel soggetto lì, per quella finestra testata, ognuno dopo l'altro ...

Infatti, percorrendo tutto il file .txt, avrai altre righe in cui potrebbe comparire questa sequenza di stringhe del tipo 

"Best Score for Window {elemento di n_windows} ".. 

Quindi, alla fine, creerò un numero di dizionari pari al numero di soggetti, ossia 

pt_1
pt_2
pt_3
pt_4
pt_5
pt_6
pt_7
pt_8
pt_9
pt_10
pt_11
pt_12
pt_13
pt_14
pt_15

dove ciascuna conterrà il numero di finestre per cui ho calcolato il best score, che sarà diversa per ogni finestra ovviamente...

quindi del tipo avrò questa costruzione di questi dizionari:

0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121

ognuna, quindi, dovrà conteggiare 

i best score ottenuti da ogni singolo soggetto, 
per quella finestra di segnale EEG, 
per il livello di ricostruzione considerato 

(che è identificato dall'aver visto se la porzione finale della stringa associata al nome del file contenga la stringa "_level_4_std" o "_level_5_std, quando iteri dentro la folder path)...


<br>

La stessa sequenza di passaggi vorrei che venisse eseguita quando si controlla che la porzione finale della stringa associata al nome del file contenga la stringa "_level_5_std" ...

quindi in quel caso creerò dizionario **best_scores_level_4_single_th**, con dentro una stessa struttura ossia


pt_1
pt_2
pt_3
pt_4
pt_5
pt_6
pt_7
pt_8
pt_9
pt_10
pt_11
pt_12
pt_13
pt_14
pt_15

ognuna con dentro 


0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121




<br>

Quindi che nel codice voglio che si prenda dal relativo file .txt del soggetto 

(per i due livelli di ricostruzione del segnale, ossia ad esempio dal primo soggetto 

"optimized_params_pt_1_level_4_std.txt"
e 
"optimized_params_pt_1_level_5_std.txt"

per ogni finestra considerata
(i.e., n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"])

il migliore best score che il soggetto 1 ha ottenuto quella finestra lì, ossia per la prima che sarà 0-50
e così via per le altre...

e che la stessa cosa la deve fare per ogni soggetto (pt_2, pt_3 etc.)


<br>
<br>
<br>


**N.B. INTEGRAZIONE AGGIUNTIVA** 

Inoltre, quello che vorrei fare io è 

1) Per **ogni soggetto**, segnarmi
  - 1.1) il **valore di best score** per quella **specifica finestra** là,
  - 1.2) la **media dei punteggi** ottenuti in quella **specifica finestra** là .
  - 1.3.) la **relativa deviazione standard** di quel best score, **rispetto a quella finestra di quel soggetto specifico**..


Perché forse così ottengo una indicazione migliore di quanto è attendibile quel punteggio per quella finestra là, per quel soggetto lì... ma solo per quel soggetto lì, ossia srebbe una deviazione standard di quella finestra, ma soggetto-specifica... giusto?


Ossia, voglio ottenere una **misura di attendibilità specifica per ogni soggetto**. 

Quindi, stai cercando di **calcolare la deviazione standard dei punteggi di best score ottenuti per ciascuna finestra di un soggetto specifico**, tra tutte le combinazioni di iper-parametri testate. 

Questo darà **un'idea di quanto varia il miglior punteggio ottenuto per quella finestra per quel soggetto**.


STEPS :

- Estrai i punteggi migliori per ogni finestra e soggetto: Raccogli i punteggi migliori ottenuti per ciascuna finestra da tutte le combinazioni testate per quel soggetto.

- Calcola la deviazione standard per ciascuna finestra e soggetto: Per ogni finestra e soggetto, calcola la deviazione standard dei punteggi migliori ottenuti dai diversi modelli. Questo ti darà una misura di quanto varia il miglior punteggio ottenuto per quella finestra.


**OBIETTIVO**

La relazione che ti interessa è 

**come il best score si confronta con la deviazione standard rispetto al punteggio medio nella finestra. 
In altre parole, vuoi capire se il best score è significativamente alto rispetto alla variabilità (deviazione standard) dei punteggi in quella finestra**


<br>


**IMPLEMENTAZIONE**

Nel file .txt ci sono delle righe  che iniziano con 

"Window 0-50	Tested Params":  dove "0-50" è una stringa dinamica, che cambia in funzione della stringa iterata dentro la variabile "n_windows" ...


ora, se trovi nella riga questa sequenza di stringhe del tipo
"Window 0-50	Tested Params" .. voglio che prendi il valore float che, in quella riga, compare dopo la scritta 'Score:'..

quel valore corrisponde al valore di score ottenuto dal modello per quella combinazione di iper-parametri testata in quel momento lì...

tu dovresti avere alla fine 100 valori di score 

(in questo caso nel file .txt dalla riga 3 alla riga 102 se il pattern di riga corrisponde a "Window 0-50	Tested Params" dove  abbiamo detto che "0-50" è una stringa dinamica, che cambia in funzione della stringa iterata dentro la variabile "n_windows" ... )  

tutti questi valori, vorrei che li appendessi in una variabile che chiameremo scores_window_{n_window} dove "{n_window}" dovrebbe corrispondere al suffisso dinamico (ossia la stringa) che dipende dalla stringa iterata dentro la variabile "n_windows"..

Quindi, in questo caso, la variabile sarebbe "scores_window_0-50" e questa conterrà tutti i valori di score rispetto ai 100 modelli ottenuti per quella finestra "0-50", compreso anche il valore di best score per ottenuto per quella finestra 0-50 per lo specifico soggetto...

ora, da questa lista "scores_window_0-50", vorrei che mi calcolassi la media e la deviazione standard..

dove il valore di media lo salverai un nuova chiave del dizionario annidato... 

ossia,
ora ad esempio hai che nel codice le chiavi di primo ordine di 

"best_scores_level_4_single_th" sono:

best_scores_level_4_single_th keys: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

quindi, dentro ad esempio al sotto-dizionario del soggetto 1 (i..e, 'th_1') oltre alle sue sotto-chiavi che contengono il best score associato a quella finestra ossia ad esempio per il primo soggetto avrai 

0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121


vorrei che mettessi un'altra chiave, che chiamerai "mean_score_window_{n_window}" dove come sempre  "{n_window}" dovrebbe corrispondere al suffisso dinamico (ossia la stringa) che dipende dalla stringa iterata dentro la variabile "n_windows".. e quindi in questo primo caso sarebbe 
  
"mean_score_window_0-50" e dentro questa chiave, voglio che tu inserisce il valore di media calcolato sui valori di score ottenuti dal soggetto 1 per la finestra 0-50, 

e la stessa cosa, per la deviazione standard, che chiamerai

"std_score_window_0-50" e dentro questa chiave, voglio che tu inserisci la deviazione standard calcolata sui valori di score ottenuti dal soggetto 1 per la finestra 0-50...

tutta questa procedura, vorrei che la facessi per tutte le finestre, di ogni soggetto..

in modo che, dentro ogni sotto-dizionario di ogni soggetto , ossia per ogni chiave di primo ordine di 

best_scores_level_4_single_th keys: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

tu inserisca altre due chiavi, accanto a quelle che già contengono il valore di best score ottenuto da quel soggetto per quella finestra, ad esempio

0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121


ci metterai accanto anche la chiave associata alla media dei valori di score per quella finestra e della deviazione standard, ossia del tipo

"th_1":

0-50: 0.2681818181818182
"mean_score_window_0-50": valore float calcolato
"std_score_window_0-50": valore float calcolato

25-75: 0.2681818181818182
"mean_score_window_25-75": valore float calcolato
"std_score_window_25-75": valore float calcolato

....

e così via...

<br>
<br>
<br>


Dobbiamo 

1) iterare tra i file per ciascun soggetto,
2) cercare le righe con il pattern dinamico Window {window} Tested Params,
3) estrarre i valori di score associati e calcolare media e deviazione standard per ciascuna finestra di tempo.
4) Questi valori verranno aggiunti come nuove chiavi nel dizionario per ogni soggetto.

Ecco come possiamo aggiornare il codice:

- Cercare le righe con "Window {window} Tested Params" ed estrarre i valori di score.
- Memorizzare i valori dei punteggi in una lista.
- Calcolare la media e la deviazione standard per ciascuna finestra.
- Aggiungere questi valori nel dizionario per ogni soggetto.



##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI - OLD VERSION**

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader


In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/


In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_pt = {}
    best_scores_level_5_single_pt = {}
    best_scores_level_5_detail_pt = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "all_pt_level_4_std" in file_name or "all_pt_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'pt_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            #if level == 4 and subject not in best_scores_level_4_single_th:
            if level == 'approx_4' and subject not in best_scores_level_4_single_pt:    
                best_scores_level_4_single_pt[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_pt:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_pt:
                best_scores_level_5_single_pt[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_pt:
                best_scores_level_5_detail_pt[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_pt[subject][window] = max(best_scores_level_4_single_pt[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_pt[subject][window] = max(best_scores_level_5_single_pt[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_pt[subject][window] = max(best_scores_level_5_detail_pt[subject][window], best_score)

    return best_scores_level_4_single_pt, best_scores_level_5_single_pt, best_scores_level_5_detail_pt  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_pt_lr, best_scores_level_5_single_pt_lr, best_scores_level_5_detail_pt_lr = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_pt_lr keys\033[0m: {best_scores_level_4_single_pt_lr.keys()}")

for pt_key, window_key in best_scores_level_4_single_pt_lr.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_pt_lr keys\033[0m: {best_scores_level_5_single_pt_lr.keys()}")

for pt_key, window_key in best_scores_level_5_single_pt_lr.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_pt_lr keys\033[0m: {best_scores_level_5_detail_pt_lr.keys()}")

for pt_key, window_key in best_scores_level_5_detail_pt_lr.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
pwd

In [ ]:

#cd ..
#cd New_Plots_Sliding_Estimator_MNE

#path corretta --> cd Plots_Sliding_Estimator_MNE
#path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"

#Comandi da eseguire

#!pwd
#cd Plots_Sliding_Estimator_MNE


import pickle

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_level_4_single_pt_lr.pkl', 'wb') as file:
    pickle.dump(best_scores_level_4_single_pt_lr, file)
    
    
# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_level_5_single_pt_lr.pkl', 'wb') as file:
    pickle.dump(best_scores_level_5_single_pt_lr, file)

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_level_5_detail_pt_lr.pkl', 'wb') as file:
    pickle.dump(best_scores_level_5_detail_pt_lr, file)


##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER EEG 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_pt = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_pt:    
                best_scores_filtered_1_20_single_pt[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_pt[subject][window] = max(best_scores_filtered_1_20_single_pt[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_pt

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_pt_lr = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_pt_lr keys\033[0m: {best_scores_filtered_1_20_single_pt_lr.keys()}")

for pt_key, window_key in best_scores_filtered_1_20_single_pt_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
#pwd
#cd ..
#cd New_Plots_Sliding_Estimator_MNE

#path corretta --> cd Plots_Sliding_Estimator_MNE
#path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"

#Comandi da eseguire

#!pwd
#cd Plots_Sliding_Estimator_MNE


import pickle

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_filtered_1_20_single_pt_lr.pkl', 'wb') as file:
    pickle.dump(best_scores_filtered_1_20_single_pt_lr, file)

#print("Dati concantenati dei Singoli Terapisti salvati in 'subject_level_concatenations_th_1_20.pkl'")

##### **Descrizione degli step nel codice per plottare le best score performances per il level 4 e 5 dalle ricostruzioni**:

###### **Arrangement of Data Structure for EACH SINGLE Patient's(PT01) accuracy score** 


- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ and δ)**

Adesso per ogni soggetto dentro i due dizionari annidati, ossia

**best_scores_level_4_single_th** e **best_scores_level_5_single_th**

voglio fare il plot che grafichi le accuratezze per ogni finestra testata di ogni soggetto.. 

Vorrei però chiederti delle modifiche, rispetto a queste modifiche che erano state fatte inizialmente, ossia:

1) Conversione dell'asse 𝑥: l'asse 𝑥 è stato generato per riflettere i millisecondi spostati di -200 ms.
2) Annotazioni sui punti temporali: le annotazioni mostrano i campioni temporali originali
3) Linea tratteggiata: Indica il 50° campione come inizio del periodo di prestimolo.


In ordine:

1) lascialo così, non toccarla

2) anziché le annotazioni che indicano il punto temporale che identifica l'inizio di ogni finestra, vorrei che mi segnassi con un carattere speciale "orizzontale" , tipo "-" il campione associato all'inizio e alla fine di ogni finestra, in modo che ci sia la corrispondenza del campione discretizzato EEG con il relativo tempo in misura di millisecondi...

tieni presente però che, 

lo spostamento di ogni finestra analizzata copre la metà della finestra precedente, perché l'intera finestra sarebbe di 50 campioni (che convertito son 200 mms), ma poi la finestra "successiva" comincia dopo i primi 25 campioni di quella precedente (quindi a metà di quella precedente!)

Ad esempio: 

La prima finestra, parte sull'asse x dal tempo 0 mms fino a 200 mms (per i primi 50 campioni discretizzati EEG)

La seconda finestra partirà dal 25° campione (quindi a metà della precedente finestra) e finirà 25 campioni (ossia 100 mms dopo) dopo la fine della prima finestra...

Quindi, devi trovare un modo di plottarmi un carattere speciale "orizzontale" , tipo "-", 

per indicare il campione associato all'inizio e alla fine di ogni finestra, tenendo conto di questa "parziale" sovrapposizione delle finestre tra di loro

inoltre, per ogni finestra, alla sua metà, disegnami un punto, 
che indicherà il valore di best score associato a quella finestra là.. 

ovviamente, tieni conto della collocazione grafica diversa (non sovrapposta) tra 

il punto che identifica il valore di best score per quella finestra lì, con 
il carattere speciale "orizzontale" , tipo "-" che rappresenterà il campione  associato all'inizio della finestra successiva...


<br>

#### Comments on Edits:


- Le annotazioni sui punti temporali adesso utilizzano un carattere speciale "orizzontale" (-) per indicare l'inizio e la fine di ogni finestra (50 campioni), considerando la sovrapposizione parziale.
  
- Viene tracciato un punto centrale per ogni finestra, che rappresenta il valore di best score per quella finestra.

- Il carattere speciale "orizzontale" viene posizionato per evitare sovrapposizioni con i punti che indicano i valori di best score.


##### **ALL SINGLE Patients (PT01-PT20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI - OLD VERSION**

##### **ALL SINGLE Patients (PT01-PT20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX & LEVEL 5 DA COEFF DETAIL DELLE RICOSTRUZIONI**

In [ ]:
!pwd

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO PAZIENTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI APPROX 4, APPROX 5 e DETAIL 5

best_scores_level_4_single_pt_lr, 
best_scores_level_5_single_pt_lr,
best_scores_level_5_detail_pt_lr
'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
     # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    pts_baseline_accuracy_highest_class_in_fold_lr = list()
    
    for subject, scores in best_scores_dict.items():
        
        '''Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_pt:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_pt[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            pts_baseline_accuracy_highest_class_in_fold_lr.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        

        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'approx_4':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta'
            clf_str = 'lr'
            
        elif level == 'approx_5':
            
            ax1.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            
            level_str = 'delta'
            clf_str = 'lr'
                
                
        elif level == 'detail_5':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta_strict'
            clf_str = 'lr'
            
        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='g', zorder=5, label=f'Best Score Logistic Regression for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='g', zorder=5, label=f'Best Score Logistic Regression for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return pts_baseline_accuracy_highest_class_in_fold_lr

# Esempio di utilizzo
save_path_level_4 = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5 = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5_detail = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
pts_baseline_accuracy_highest_class_in_fold_level_4_lr = plot_best_scores_for_subjects(best_scores_level_4_single_pt_lr, 'approx_4', save_path_level_4)
pts_baseline_accuracy_highest_class_in_fold_level_5_lr = plot_best_scores_for_subjects(best_scores_level_5_single_pt_lr, 'approx_5', save_path_level_5)
pts_baseline_accuracy_highest_class_in_fold_level_5_detail_lr = plot_best_scores_for_subjects(best_scores_level_5_detail_pt_lr, 'detail_5', save_path_level_5)

In [ ]:
!pwd

In [ ]:
# Salvare l'intero dizionario annidato con pickle


# Salvare l'intero dizionario annidato con pickle
import pickle

with open('best_scores_level_4_single_pt_lr.pkl', 'wb') as f:
    pickle.dump(best_scores_level_4_single_pt_lr, f)

with open('best_scores_level_5_single_pt_lr.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_single_pt_lr, f)
    
with open('best_scores_level_5_detail_pt_lr.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_detail_pt_lr, f)

##### **ALL SINGLE Patients (PT01-PT20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)

In [ ]:
#new_subject_level_concatenations_pt_1_20.keys()

In [ ]:
#new_subject_level_concatenations_pt_1_20.keys()
#dict_keys(['pt_1', 'pt_2', 'pt_3', 'pt_4', 'pt_5', 'pt_6', 'pt_7', 'pt_8', 'pt_9', 'pt_10', 'pt_11', 'pt_12', 'pt_13', 'pt_14', 'pt_15', 'pt_16'])

#new_subject_level_concatenations_pt_1_20['pt_16'].keys()
#dict_keys(['data', 'labels'])

In [ ]:
!pwd

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO PAZIENTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI FILTERED 1-20Hz

best_scores_filtered_1_20_single_pt_lr

'''


import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
    # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots_1_20')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    pts_baseline_accuracy_highest_class_in_fold_lr = list()
    
    for subject, scores in best_scores_dict.items():
        
        '''Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}_filtered_1_20')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_pt_1_20:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_pt_1_20[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            pts_baseline_accuracy_highest_class_in_fold_lr.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        
        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'filtered_1_20':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)',  fontsize = 16)
            
            level_str = 'filtered_1_20'
            clf_str = 'lr'
            

        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='g', zorder=5, label=f'Best Score Logistic Regression for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='g', zorder=5, label=f'Best Score Logistic Regression for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return ths_baseline_accuracy_highest_class_in_fold_lr

# Esempio di utilizzo
save_path_filtered_1_20 = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
pts_baseline_accuracy_highest_class_in_fold_1_20_lr = plot_best_scores_for_subjects(best_scores_filtered_1_20_single_pt_lr, 'filtered_1_20', save_path_filtered_1_20)


#### **All Patients (PT01-PT20)**

#### Plots of **Grand Average Mean** of Best Single Subject's Accuracy Score Performances 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **NEW VERSION**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_pt = {}
    best_scores_level_5_single_pt = {}
    best_scores_level_5_detail_pt = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_pt_level_4_std" o "all_pt_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_pt_level_4_std" o "all_pt_level_5_std"
            if "all_pt_level_4_std" in file_name or "all_pt_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            #if level == 4 and subject not in best_scores_level_4_single_pt:
            
            if level == 'approx_4' and subject not in best_scores_level_4_single_pt:    
                best_scores_level_4_single_pt[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_pt:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_pt:
                best_scores_level_5_single_pt[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_pt:
                best_scores_level_5_detail_pt[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_pt[subject][window] = max(best_scores_level_4_single_pt[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_pt[subject][window] = max(best_scores_level_5_single_pt[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_pt[subject][window] = max(best_scores_level_5_detail_pt[subject][window], best_score)

    return best_scores_level_4_single_pt, best_scores_level_5_single_pt, best_scores_level_5_detail_pt  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_pt_lr, best_scores_level_5_single_pt_lr, best_scores_level_5_detail_pt_lr = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_pt_lr keys\033[0m: {best_scores_level_4_single_pt_lr.keys()}")

for th_key, window_key in best_scores_level_4_single_pt_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_pt_lr keys\033[0m: {best_scores_level_5_single_pt_lr.keys()}")

for th_key, window_key in best_scores_level_5_single_pt_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_pt_lr keys\033[0m: {best_scores_level_5_detail_pt_lr.keys()}")

for th_key, window_key in best_scores_level_5_detail_pt_lr.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        '''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")

        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_4 = calculate_mean_and_confidence_interval(best_scores_level_4_single_pt_lr, n_windows)
statistics_level_5 = calculate_mean_and_confidence_interval(best_scores_level_5_single_pt_lr, n_windows)
statistics_level_5_detail = calculate_mean_and_confidence_interval(best_scores_level_5_detail_pt_lr, n_windows)

In [ ]:
'''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
#print(best_scores_level_4_single_pt_lr['pt_1']['0-50'])
#print(best_scores_level_4_single_pt_lr['pt_2']['0-50'])
#print(best_scores_level_4_single_pt_lr['pt_3']['0-50'])
#print()
#print(best_scores_level_4_single_pt_lr['pt_1']['25-75'])
#print(best_scores_level_4_single_pt_lr['pt_2']['25-75'])
#print(best_scores_level_4_single_pt_lr['pt_3']['25-75'])

In [ ]:
type(statistics_level_4)

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
!pwd

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('new_all_pt_concat_reconstructions.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_pt['pt_1'].keys()

In [ ]:
new_all_pt_concat_reconstructions.keys()

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME '''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    subjects_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    os.makedirs(subjects_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 4:
        level_str = 'theta'
    elif level == 5:
        level_str = 'delta'
    elif level == '5_detail':
        level_str = 'theta_strict'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'all_ths_level_{level_str}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    print(f"\n\t\t\t\t\t\033[1mPatients'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_pt_concat_reconstructions.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    
    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)

    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Aggiunge il livello di baseline in base al livello specificato
    #if level == 4:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range')
    #elif level == 5:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range')
    #elif level == '5_detail':
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Detail Range')
    
    '''VECCHIO'''
    
    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
    if level_str == 'theta':
        ax1.set_title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range', fontsize = 16)
        ax2.set_title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range',  fontsize = 16)
        
    elif level_str == 'delta':
        ax1.set_title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)
        ax2.set_title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)

    elif level_str == 'theta_strict':
        ax1.set_title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
        ax2.set_title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
    
    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='g', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='g', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='g', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='g', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_pts_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(subjects_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_4, 4, save_path)
plot_mean_best_scores_for_window(statistics_level_5, 5, save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail, '5_detail', save_path)

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE E PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    

 # Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_all_pt_concat_reconstructions_1_20.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions_1_20 = pickle.load(f)

In [ ]:
print(new_subject_level_concatenations_pt_1_20.keys())
print()
print(new_subject_level_concatenations_pt_1_20['pt_1'].keys())
print(new_subject_level_concatenations_pt_1_20['pt_1']['data'].shape)
print()
print(new_all_pt_concat_reconstructions_1_20.keys())
print(new_all_pt_concat_reconstructions_1_20['data'].shape)

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''

import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_pt = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_pt:    
                best_scores_filtered_1_20_single_pt[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_pt[subject][window] = max(best_scores_filtered_1_20_single_pt[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_pt

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_pt_lr = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_pt_lr keys\033[0m: {best_scores_filtered_1_20_single_pt_lr.keys()}")

for pt_key, window_key in best_scores_filtered_1_20_single_pt_lr.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_1_20 = calculate_mean_and_confidence_interval(best_scores_filtered_1_20_single_pt_lr, n_windows)

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

unfamiliar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    data_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    os.makedirs(data_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 'filtered_1_20':
        level_str = 'filtered_1_20'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    #print(f"\n\t\t\t\t\t\033[1mPatients'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_pt_concat_reconstructions_1_20.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}\n\n\n")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    
    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)
    
    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Linea orizzontale per il chance level
    #plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    #plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)')

    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è filtered_1_20, gestisci i titoli per i grafici su ax1 e ax2
    if level == 'filtered_1_20':

        ax1.set_title(f'Logistic Regression - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 14)
        ax2.set_title(f'Logistic Regression - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 14)

    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='g', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='g', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='g', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='g', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_pts_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(data_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'\nPlot salvato in: \n\033[1m{save_file_path}\033[0m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_1_20, 'filtered_1_20', save_path)

## **XGBoost**

##### **NOTA BENE**

È importante notare che **se stai applicando filtri EEG diversi ai dati** o se i dati stessi sono diversi, **potrebbe essere consigliabile eseguire la ricerca degli iperparametri ogni volta**!

**Questo perché i migliori iperparametri possono variare in base alle caratteristiche specifiche dei dati o delle trasformazioni che applichi ad essi**. 

Se hai la possibilità di fare la random search di nuovo ogni volta che cambi i dati, **otterrai modelli ottimizzati per le nuove condizioni specifiche**.

In definitiva, la scelta dipende dalla tua situazione specifica e dalle tue esigenze. Se sei sicuro che i dati e le trasformazioni rimarranno gli stessi, salvare e riutilizzare il modello migliore può risparmiarti tempo e risorse computazionali. 

Tuttavia, se ci sono variazioni nei dati o nelle trasformazioni, può essere più prudente eseguire nuovamente la ricerca degli iperparametri per ottenere risultati ottimali.

<br>

Il **tempo di esecuzione** tra **XGBoost** e **Logistic Regression** può variare significativamente per diversi motivi, anche se entrambi sono modelli di machine learning per la classificazione. Ecco alcune ragioni principali che possono influenzare il tempo di esecuzione:

- **Complessità dell'algoritmo**: XGBoost è noto per essere computazionalmente più intensivo rispetto alla Logistic Regression. XGBoost utilizza il boosting degli alberi decisionali, che comporta l'addestramento sequenziale di molti alberi, ognuno dei quali viene ottimizzato iterativamente per migliorare la precisione complessiva del modello. Questo processo può richiedere più tempo rispetto alla Logistic Regression, che è un modello più semplice basato su una funzione lineare.

- **Dimensione dei dati**: Se hai un numero elevato di feature (ad esempio, molti canali EEG e time points nel tuo caso), XGBoost può richiedere più tempo per addestrarsi rispetto alla Logistic Regression. Questo perché XGBoost deve esplorare un numero maggiore di possibili suddivisioni dell'albero e ottimizzare parametri più complessi rispetto alla regressione logistica, che è più diretta nei suoi calcoli.

- **Complessità del problema**: XGBoost può essere più adatto a problemi con relazioni non lineari tra le variabili di input e l'output, mentre la regressione logistica funziona bene quando le relazioni sono più semplici e lineari. Se il tuo problema richiede l'apprendimento di relazioni complesse o non lineari, XGBoost potrebbe essere preferito nonostante il tempo di addestramento più lungo.

- **Parametri e ottimizzazione**: XGBoost ha più iperparametri da ottimizzare rispetto alla regressione logistica. Questo significa che durante la ricerca di parametri ottimali tramite tecniche come la RandomizedSearchCV, XGBoost potrebbe richiedere più iterazioni e quindi più tempo di calcolo rispetto alla regressione logistica, che ha meno iperparametri rilevanti da configurare.

 - **Parallelizzazione**: Anche se entrambi i modelli supportano l'addestramento parallelo, la configurazione e la gestione della parallelizzazione possono influenzare il tempo di esecuzione. XGBoost, essendo più complesso, potrebbe non sempre beneficiare della parallelizzazione in modo diretto come la regressione logistica, dove le operazioni matematiche sono più semplici da parallelizzare.

In sintesi, il tempo di esecuzione dipende da molti fattori, tra cui la complessità dell'algoritmo, la dimensione dei dati, la complessità del problema e la configurazione dei parametri. XGBoost può richiedere più tempo di addestramento rispetto alla regressione logistica a causa della sua natura più complessa e della necessità di ottimizzare una serie di parametri per raggiungere prestazioni ottimali.

##### **Selezione valori migliori per set iper-parametri**

<br>

**IO**

Mi serve capire quali sono i **limiti accettabili per le combinazioni di iper-parametri valide o meno**, 
devo capire dalla **documentazione di xgboost** quali sono i **valori accettabili per ogni iper-parametro** 
e fare in modo che il **blocco try-except del mio codice gestisca le combinazioni di iper-parametri che eventualmente producano incompatibilità tra i diversi iper-parametri**

<br>

**CHAT**

In linea di principio, se imposti valori validi per ogni iper-parametro di XGBoost, non dovresti incontrare errori di configurazione, purché questi valori rispettino i vincoli del modello.

Tuttavia, XGBoost può generare errori o avvisi quando certe combinazioni di iper-parametri sono tecnicamente valide, ma non sono efficaci o causano problemi durante l'addestramento. Ecco alcuni casi comuni:

1. **max_depth troppo alto**:
Un valore molto alto per max_depth (ad esempio, >15) può portare a modelli estremamente complessi e richiedere molta memoria, oltre a un notevole tempo di addestramento. Anche se non è tecnicamente un errore, può far fallire l'addestramento per mancanza di memoria (out-of-memory).
2. **colsample_bytree e subsample troppo bassi**:
Se imposti colsample_bytree o subsample a valori molto bassi (vicino a 0), la quantità di dati selezionata per la costruzione degli alberi sarà troppo ridotta, portando a modelli inefficienti o errori di addestramento.
Ad esempio, colsample_bytree=0.1 o subsample=0.1 significa che stai addestrando alberi su solo il 10% dei dati disponibili, il che può causare errori di convergenza o rendere il modello incapace di apprendere correttamente.
3. **learning_rate troppo basso o troppo alto**:
Un valore di learning_rate troppo basso (ad esempio, 0.0001) può richiedere migliaia di iterazioni per convergere, rallentando l'addestramento. Al contrario, un valore troppo alto (ad esempio, 1.0) può causare instabilità e far sì che il modello non converga mai.
4. **gamma troppo alto**:
gamma è il parametro che controlla il minimo guadagno di scissione. Un valore troppo alto può inibire la costruzione degli alberi, perché il modello non aggiungerà nuovi split, causando un comportamento in cui il modello smette di apprendere.
5. **n_estimators troppo alto**:
Un numero di alberi troppo alto (es. 10.000 alberi) può essere inefficiente in termini di tempo e risorse. Anche se non fallirà tecnicamente, richiederà troppo tempo.
6. **Incompatibilità tra iper-parametri**:
Alcuni parametri non hanno combinazioni efficienti. Ad esempio, un max_depth molto alto combinato con un learning_rate molto basso può rendere l'addestramento del modello molto lento senza alcun vantaggio significativo.
7. **Out-of-Bounds Values**:
Se assegni un valore fuori dai limiti accettabili per un parametro (ad esempio, max_depth negativo), questo può causare un errore immediato. La documentazione di XGBoost definisce i limiti accettabili per ogni iper-parametro.
Gestione di combinazioni problematiche
Un buon approccio è usare la ricerca casuale con un intervallo di iper-parametri ragionevole. Tuttavia, se il numero di combinazioni è elevato e il tempo di addestramento diventa troppo lungo, potresti riscontrare combinazioni subottimali che non offrono miglioramenti.

In pratica, quindi, non tutte le combinazioni sono "non valide" nel senso di generare errori, ma molte combinazioni possono portare a modelli scadenti, overfitting, underfitting o tempi di addestramento molto lunghi.

Se mi mostri il codice, posso suggerirti come ottimizzare il controllo di queste combinazioni e commentare eventuali punti di attenzione.


<br>
<br>


Mi sai indirizzare alla **pagina della documentazione di XGBoost** che definisce i **limiti accettabili per ogni iper-parametro**?

You can find the detailed documentation on XGBoost's hyperparameters, including acceptable ranges and default values, in the official XGBoost documentation. 

This section outlines the limits and settings for parameters such as eta, max_depth, colsample_bytree, min_child_weight, and others.

You can explore this further on the XGBoost parameter documentation page here​(XGBoost Read the Docs):

- **https://xgboost.readthedocs.io/en/stable/parameter.html**
- **https://xgboost.readthedocs.io/en/stable/**

This page provides all the details you need to fine-tune your model.








#### **ALL SINGLE Therapists (TH01-TH20)**

#### Automatization of all steps from: 

1) "**subject_level_concatenations_th**" : ricostruzioni 4 e 5° livello wavelet da approx coefficients
2) "**new_subject_level_concatenations_th**":  ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_th_1_20**": EEG preprocessed signal filtered 1-20Hz 


In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    
#subject_level_concatenations_th.keys()

##### **ALL SINGLE Therapists (TH01-TH15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DELLE RICOSTRUZIONI**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**

In [ ]:
''' XGBOOST --> TERAPISTI GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.

'''


# Prepare a series of classifier applied to 50 time samples window with 25 stride

#XGBoost
#To use xgb.XGBClassifier in your project, 
#you can refer to the XGBoost documentation. 
#XGBClassifier is a part of the XGBoost library, designed for classification tasks using gradient boosting.

'''
Yes, you can use XGBoost for multi-class classification. 

The xgb.XGBClassifier supports multi-class classification 
by setting the objective parameter to multi:softmax or multi:softprob. 

Here’s how you can set it up:
- multi:softmax: Sets the classifier to output the class with the highest predicted probability.
- multi:softprob: Sets the classifier to output the predicted probabilities of each class.

https://xgboost.readthedocs.io/en/stable/python/python_api.html#xgboost.XGBClassifier
'''

#Per trovare migliori iperametri per Xgboost

#Google Scholar: best hyperparametrs for xgboost classification
#https://scholar.google.com/scholar?hl=it&as_sdt=0%2C5&q=best+hyperparametrs+for+xgboost+classification&btnG=&oq=best+hyperparametrs+for+XGBoost+classi

#https://arxiv.org/pdf/1901.08433
#https://dl.acm.org/doi/abs/10.1145/3297067.3297080


import numpy as np
import time
import torch

from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler

from xgboost import XGBClassifier

import joblib
import json
import os



param_distributions = {
    "learning_rate": [float(x) for x in (np.arange(0.005, 0.301, 0.05))],  # Da 0.005 a 0.3 con passo 0.05
    "subsample": [float(x) for x in (np.arange(0.8, 1.05, 0.05))],        # Da 0.8 a 1 con passo 0.05
    "max_leaves": [int(x) for x in (np.arange(10, 51, 5))],             # Da 10 a 50 con passo 5
    "max_depth": [int(x) for x in (np.arange(5, 31, 5))],              # Da 5 a 30 con passo 5
    "gamma": [float(x) for x in (np.arange(0, 0.03, 0.005))],            # Da 0 a 0.03 con passo 0.005
    "colsample_bytree": [float(x) for x in (np.arange(0.8, 1.05, 0.05))], # Da 0.8 a 1 con passo 0.05
    "min_child_weight": [int(x)for x in (np.arange(1, 11, 1))]}       # Da 1 a 10 con passo 1




# Itera attraverso i soggetti

'''OLD VERSION'''
#for subject, levels in subject_level_concatenations_th.items():


'''NEW VERSION'''

for subject, levels in new_subject_level_concatenations_th.items():
    
    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO'''   
    
    #if subject == 'th_16':
    #if subject == 'th_17' or subject == 'th_18' or subject == 'th_19':
    
    if subject == 'th_20':
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")


        '''NEW VERSION'''
        #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
        params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params'

        # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
        #                                      'delta' = δ,i.e., approx_5 ,
        #                                      'theta_strict' = Θ, i.e., detail_5,
        #                                      'labels') 

        for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'


            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")

            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_std.txt'

            #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\t\033[1m{params_dir}\033[0m"),
            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

            y = levels['labels'] # Estraiamo le labels livello corrente del soggetto corrente


            #Path per combinazioni iperparametri NON valide
            #invalid_params_file_path = f'{params_dir}/invalid_params_{subject}_level_{level}_std.txt'

            print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE XGBOOST


            base_clf = XGBClassifier (objective = 'multi:softmax', use_label_encoder = False, eval_metric = 'logloss')

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            #invalid_combination_count = 0

            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")


                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_clf,
                        param_distributions = param_distributions,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:

                        for i, params in enumerate(rand_search.cv_results_['params']):


                            #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                            #calcolato sulla base di una cross-validation a 5 fold. 
                            #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                            #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                            #In sintesi, è il valore medio di accuracy ottenuto 
                            #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                            #per una specifica combinazione di iper-parametri!


                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                invalid_combination_count += 1
                                print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri

                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH

                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")

##### **ALL SINGLE Therapists (TH01-TH16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

- **EEG preprocessed signal**: filtered 1-20


In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun soggetto nel dizionario
for soggetto, dati in new_subject_level_concatenations_th_1_20.items():
    
    # Verifica che 'data' sia presente tra le chiavi
    if 'data' in dati:
        
        # Sotto-seleziona i canali di interesse
        dati_originali = dati['data']  # Estrai i dati
        
        dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali

        # Aggiorna la chiave 'data' con i dati filtrati
        new_subject_level_concatenations_th_1_20[soggetto]['data'] = dati_sottoselezionati

        # Opzionale: stampa di controllo per verificare la nuova forma dei dati
        print(f"Soggetto {soggetto}: {dati_sottoselezionati.shape}")

In [ ]:
for subject, levels in new_subject_level_concatenations_th_1_20.items():
    print(type(levels['labels']))

In [ ]:
##### **ALL SINGLE Therapists (PT01-PT15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DAL SEGNALE 1-20Hz**


''' XGBOOST --> TERAPISTI GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.

'''


# Prepare a series of classifier applied to 50 time samples window with 25 stride

#XGBoost
#To use xgb.XGBClassifier in your project, 
#you can refer to the XGBoost documentation. 
#XGBClassifier is a part of the XGBoost library, designed for classification tasks using gradient boosting.

'''
Yes, you can use XGBoost for multi-class classification. 

The xgb.XGBClassifier supports multi-class classification 
by setting the objective parameter to multi:softmax or multi:softprob. 

Here’s how you can set it up:
- multi:softmax: Sets the classifier to output the class with the highest predicted probability.
- multi:softprob: Sets the classifier to output the predicted probabilities of each class.

https://xgboost.readthedocs.io/en/stable/python/python_api.html#xgboost.XGBClassifier
'''

#Per trovare migliori iperametri per Xgboost

#Google Scholar: best hyperparametrs for xgboost classification
#https://scholar.google.com/scholar?hl=it&as_sdt=0%2C5&q=best+hyperparametrs+for+xgboost+classification&btnG=&oq=best+hyperparametrs+for+XGBoost+classi

#https://arxiv.org/pdf/1901.08433
#https://dl.acm.org/doi/abs/10.1145/3297067.3297080


import numpy as np
import time
import torch

from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler

from xgboost import XGBClassifier

import joblib
import json
import os



param_distributions = {
    "learning_rate": [float(x) for x in (np.arange(0.005, 0.301, 0.05))],  # Da 0.005 a 0.3 con passo 0.05
    "subsample": [float(x) for x in (np.arange(0.8, 1.05, 0.05))],        # Da 0.8 a 1 con passo 0.05
    "max_leaves": [int(x) for x in (np.arange(10, 51, 5))],             # Da 10 a 50 con passo 5
    "max_depth": [int(x) for x in (np.arange(5, 31, 5))],              # Da 5 a 30 con passo 5
    "gamma": [float(x) for x in (np.arange(0, 0.03, 0.005))],            # Da 0 a 0.03 con passo 0.005
    "colsample_bytree": [float(x) for x in (np.arange(0.8, 1.05, 0.05))], # Da 0.8 a 1 con passo 0.05
    "min_child_weight": [int(x)for x in (np.arange(1, 11, 1))]}       # Da 1 a 10 con passo 1



# Itera attraverso i soggetti

#for subject, levels in subject_level_concatenations_th_1_20.items():
for subject, levels in new_subject_level_concatenations_th_1_20.items():
    
    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO'''   
    
    #if subject == 'th_16':
    #if subject == 'th_17' or subject == 'th_18' or subject == 'th_19':
    
    #if subject == 'th_20':
        
    print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")

    print(f"\n\n\033[1mExtraction of Data\033[0m from Subject \033[1m{subject}\033[0m from Original Filtered Signal in \033[1m1-20Hz\033[0m")

    X = levels['data'] # Estraiamo i dati del soggetto corrente

    y = levels['labels'] # Estraiamo le labels livello corrente del soggetto corrente

    #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
    params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20'

    #FILE PATH DINAMICA PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
    #A SECONDA DEL SOGGETTO E LIVELLO DI RICOSTRUZIONE DEI DATI PRESI IN ESAME 

    # Costruzione del percorso del file in maniera dinamica
    params_file_path = f'{params_dir}/optimized_params_{subject}_filtered_1_20_std.txt'


    if not os.path.exists(params_dir):
        os.makedirs(params_dir)

    #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\033[1m{params_dir}\033[0m"),
    #print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

    #Path per combinazioni iperparametri NON valide
    invalid_params_file_path = f'{params_dir}/invalid_params_{subject}_filtered_1_20_std.txt'

    print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

    y = y.astype(int) 

    print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


    # Calcola il numero totale di etichette livello 4/5°
    label_counts = np.unique(y, return_counts = True)[1]
    total_labels = len(y)

    # Calcola la percentuale di ciascuna classe
    class_proportions = label_counts / total_labels * 100

    print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

    # Calcola i pesi delle classi come l'inverso delle proporzioni
    class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

    # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
    class_weights /= class_weights.sum()

    print(f"\n\033[1mClass Weights {class_weights}\033[0m")

    # Crea un dizionario per class_weight
    class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


    '''INIZIALIZZAZIONE XGBOOST'''


    base_clf = XGBClassifier (objective = 'multi:softmax', use_label_encoder = False, eval_metric = 'logloss')

    # Memorizza il tempo di inizio
    start_time = time.time()

    # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
    execution_times = []

    # Contatori per combinazioni valide e non valide
    valid_combination_count = 0
    invalid_combination_count = 0

    # File di output per i parametri ottimizzati
    with open(params_file_path, 'w') as f:
        f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

    # File di output per i parametri ottimizzati NON validi
    with open(invalid_params_file_path, 'w') as invalid_f:
        invalid_f.write(f"Invalid Parameter Combinations\n\n")


    '''INIZIALIZZAZIONE RANDOM SEARCH'''

    # Lista per memorizzare i risultati delle finestre
    window_results = []

    # Creazione della finestra scorrevole con step e dimensioni desiderate
    n_samples = X.shape[2]
    window_size = 50
    step_size = 25
    n_windows = (n_samples - window_size) // step_size + 1


    #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

    # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

    for window_start in range(0, n_samples - window_size + 1, step_size):

        # Memorizza il tempo di inizio per il punto temporale corrente
        time_point_start = time.time()

        # Definiamo la finestra corrente
        window_end = window_start + window_size

        print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

        X_window = X[:, :, window_start:window_end]
        print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

        # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
        X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
        print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

        # Standardizza i dati della finestra corrente
        scaler = StandardScaler()
        X_window_standardized = scaler.fit_transform(X_window_reshaped)
        print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")


        try:
            print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


            rand_search = RandomizedSearchCV(
                estimator = base_clf,
                param_distributions = param_distributions,
                scoring ='accuracy',
                n_iter = 100,
                verbose = 1,
                n_jobs = -1
            )


            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

            # Esegui RandomizedSearchCV sulla finestra corrente
            rand_search.fit(X_window_standardized, y)


            # Controlla il numero totale di combinazioni testate
            total_combinations_tested = len(rand_search.cv_results_['params'])
            #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

            # Salva tutte le combinazioni testate per la finestra corrente
            with open(params_file_path, 'a') as f:

                for i, params in enumerate(rand_search.cv_results_['params']):

                    '''
                    Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                    calcolato sulla base di una cross-validation a 5 fold. 
                    Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                    fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                    In sintesi, è il valore medio di accuracy ottenuto 
                    mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                    per una specifica combinazione di iper-parametri!
                    '''

                    score = rand_search.cv_results_['mean_test_score'][i]
                    f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                for params in rand_search.cv_results_['params']:
                    if params:
                        valid_combination_count += 1
                    else:
                        invalid_combination_count += 1
                        print(f"Invalid combination found: {params}")

                #QUI

                # Ottieni il modello con i migliori iper-parametri

                best_model_params = rand_search.best_params_


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH

                best_score = rand_search.best_score_


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                # Memorizza i risultati della finestra corrente
                window_results.append({
                    'window_start': window_start,
                    'window_end': window_end,
                    'best_params': best_model_params,
                    'best_score': best_score
                })


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

            #Salva i parametri migliori per la finestra corrente in una riga del file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                f.write('\n')

        except Exception as e:

            print(f'Error: {e}')

            # Scrivi la combinazione non valida nel file di output
            with open(invalid_params_file_path, 'a') as invalid_f:
                invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
            continue


            # Memorizza il tempo di fine per il punto temporale corrente
            time_point_end = time.time()

            # Calcola il tempo di esecuzione per il punto temporale corrente
            time_point_elapsed = time_point_end - time_point_start

            # Aggiungi il tempo di esecuzione alla lista
            execution_times.append(time_point_elapsed)

            # Stampa i risultati per il punto temporale corrente
            #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
            #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
            #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
            #print()
            #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
            #print()

    # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

    # Definisci il range generale delle finestre che vuoi analizzare
    general_range = [0, 300]  # Puoi modificare il range se necessario

    # Filtra i risultati delle finestre nel range desiderato
    general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

    # Controlla se ci sono risultati validi all'interno del range specificato
    if general_results:

        # Trova la finestra con il punteggio migliore
        best_general_window = max(general_results, key=lambda x: x['best_score'])

        # Trova i parametri migliori per questa finestra specifica (se disponibili)
        best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
        best_general_window['best_params'] = best_params

        # Stampa le informazioni sulla finestra migliore trovata
        #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
        #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
        #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

    else:
        print("No valid windows found in the specified range.")


    # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
    window_results.append({
        'Best window_start': best_general_window['window_start'] if general_results else None,
        'Best window_end': best_general_window['window_end'] if general_results else None,
        'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
        'best_score': best_general_window['best_score'] if general_results else None
    })

    # Calcola il tempo di esecuzione totale
    end_time = time.time()
    total_execution_time = end_time - start_time

    #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
    #print()
    #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
    #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

    # Aggiungi il risultato della migliore finestra generale al file di testo
    with open(params_file_path, 'a') as f:
        f.write('\n')
        if general_results:
            best_general_window = max(general_results, key=lambda x: x['best_score'])
            f.write(f"BEST WINDOW OVERALL: "),
            f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
            f.write(f"\nBest Window End: {best_general_window['window_end']}"),
            f.write(f"\nBest Score: {best_general_window['best_score']}")

            if best_general_window['best_params'] is not None:
                    f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
            else:
                f.write("No valid windows found in the specified range.\n")

            f.write('\n')
            f.write(f"Total execution time: {total_execution_time} seconds\n")
            f.write(f"Number of valid combinations: {valid_combination_count}\n")
            f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")            

#### **ALL SINGLE Therapists (TH01-TH20) for **COUPLED EXPERIMENTAL CONDITIONS****

#### Automatization of all steps from: 

1) "**new_subject_level_concatenations_coupled_exp_th**" ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_coupled_exp_th_1_20**": EEG preprocessed signal filtered 1-20Hz 

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''


#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
#    new_subject_level_concatenations_th = pickle.load(f)
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle
import numpy as np


with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th_1_20 = pickle.load(f)
    


    
    
#PER SALVARE I FILE
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('NOME DEL FILE.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations, f)


#subject_level_concatenations_th['th_1'].keys()

In [ ]:
print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_th\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()}")

In [ ]:
np.unique(new_subject_level_concatenations_coupled_exp_th['th_16']['theta']['baseline_vs_th_resp']['labels'],return_counts=True)

##### **Descrizione degli step nel codice per ottenere e salvare nelle paths le best score performances per il level 4 e 5 dalle ricostruzioni**:

Vorrei in questo caso, per velocizzare, iterare su 

subject_level_concatenations, che ha questa struttura...

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


al cui interno ha per ogni chiave di primo ordine, un altro dizionario annidato, che è fatto di queste chiavi


dict_keys(['theta', 'delta', 'labels'])

dentro 'theta' e 'delta' ci sono tutti i dati di tutte le condizioni sperimentali del singolo soggetto

del tipo 'theta' o 'delta' conterrà un array con shape

(204, 3, 300)

con 1° dimensione i trial, poi i canali, poi i punti di ogni trial (campioni EEG)

e dentro 'labels' ho invece l'array delle labels concatenate...
(204,)


<br>


Ora però, vorrei che ... 

Se ad esempio nel soggetto 'th_1' entri nella chiave 'theta', 

allora poi il file corrispondente .txt deve essere scritto con una path dinamica, che cambia a seconda 
- sia del soggetto iterato
- sia del livello di ricostruzione dei dati

Ossia:

la "params_dir" è fissa

mentre 

"params_file_path" è dinamica, e cambia a seconda del soggetto iterato e del livello. 

Per cui sarà una composizione di stringhe fisse e stringhe 'mobili', ossia

'params_file_path' = 'optimized_params_' + {subject} dove subject dovrebbe essere una lista di stringhe che si preleva dalle chiavi di primo ordine di "subject_level_concatenations" che erano

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


seguito da "_level_{level}_std" dove {level} dipende dal nome della chiave del sotto-dizionario iterato per ogni soggetto...

Ossia, ad esempio dentro il sotto-dizionario del primo soggetto di "subject_level_concatenations" cioè

subject_level_concatenations['th_1'], 

Se la sua sotto-chiave è 'theta' allora il level = 4, se la chiave è 'delta' allora il level = 5, 



Quindi la costruzione finale della path dinamica del file specifico per il soggetto 1 deve essere

 
params_file_path = 'optimized_params_' +'{subject}' + "_level_{level}_std.txt"

e sarà se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_1' + "_level_4_std.txt"


e sarà se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_1' + "_level_5_std.txt"


in questo modo, farei un loop unico su tutte le sottochiavi dei dizionari annidati dentro 
"subject_level_concatenations" 

ossia 
dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

e per ognuno vedo se la sua sotto-chiave sarà 'theta' o 'delta' e creerà dei file .txt corrispondenti nella param_dir che gli ho chiesto...

Il resto del codice non toccarlo invece, perché dovrebbe creare dei file .txt per ogni soggetto per ogni livello di ricostruzione dei dati,
e salverà le analisi nel file .txt corrispondente



Ad esempio, continuando col soggetto 2:

la costruzione finale della path dinamica del file specifico per il soggetto 2

Sarà, se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_2' + "_level_4_std.txt"


e sarà, se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_2' + "_level_5_std.txt"


e così via per tutti gli altri soggetti




##### **ALL SINGLE Therapists (TH01-TH16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DALLE RICOSTRUZIONI** 

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**


###### **ISTRUZIONI PER MODIFICHE AL CASO 2 CLASSI**

Allora, andiamo per step:

**1)** la nuova variabile sulla quale iterare è new_subject_level_concatenations_coupled_exp_th

che è fatta con questa struttura

print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_th\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()}")

OUTPUT:

Dataset Organization: new_subject_level_concatenations_coupled_exp_th

First Order Key: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16'])

Second Order Key: dict_keys(['theta', 'delta', 'theta_strict'])

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

Fourth Order Key: dict_keys(['data', 'labels'])

quindi significa che, per ogni soggetto, tu dovrai entrare nella sotto sotto chiave relativa ai livelli di ricostruzione del segnale 

dict_keys(['theta', 'delta', 'theta_strict'])

per ognuna di queste, avrai appunto delle altre sotto-sotto-sotto chiavi, che sono le condizioni sperimentali, sulle quali dovrai entrare che sono 

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

dopodiché dentro ognuna di queste, dovrai entrare ulteriormente dentro ciascuna sotto chiave di quarto livello:

la prima, che fa riferimento ai dati('data') il cui valore (array numpy() verrà assegnato ad X nel codice, e 
la seconda, la chiave delle labels ('labels') il cui valore verrà assegnato ad Y...

**2)** questa parte relativa ai print

 for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'

voglio che poi abbia degli altri if, nel senso che vorrei che iterando su ogni livello, voglio che venga applicata la stessa logica dei printing di qui sopra, ma alle chiavi del 3° livello, ossia quelle che fanno riferimento alle condizioni sperimentali...

ossia, 

voglio che ci sia scritto per le X

print(f"\n\033[1mExtraction of Data\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

e voglio che ci sia scritto per le Y

print(f"\n\033[1mExtraction of Labels\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

dove 

"experimental_condition" farà riferimento alla chiave della condizione sperimentale iterata in quel loop, e 

"level_key" invece farà riferimento alle chiavi del 2° livello, ossia a quelle che si riferiscono allo specifico livello di ricostruzione del segnale per il quale io sto estraendo i dati e le labels al ciclo corrente...

In questo modo, dovrei avere un'idea dai print del mio codice, quando viene eseguito, su quale soggetto, quale livello e quale condizione sperimentale sta eseguendo i calcoli.. 

**3)** voglio che vengano create dei folder nuovi per appendere i risultati di tutte le elaborazioni da parte dei vari modelli e che saranno queste due cartelle

"EEG_50_window_25_overlap_coupled_exp_cond" 
"single_therapist_optimized_params_coupled_exp_cond"
 
ossia la mia directory dovrebbe diventare

params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond'

per cui, se "EEG_50_window_25_overlap_coupled_exp_cond" né "single_therapist_optimized_params_coupled_exp_cond" non sono state create, allora andranno create...

**4)** la creazione del nome del file relativo ad un determinato soggetto dovrà essere formato in questo modo

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

dove, ricorda, "experimental_condition" farà riferimento alle insieme delle stringhe che compongono la chiave della condizione sperimentale iterata in quel loop (chiavi di 3° livello di "new_subject_level_concatenations_coupled_exp_th" 

del tipo potrebbe essere

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

Con ad esempio:

subject = th_1
level = theta 
experimental_condition = baseline_vs_th_resp

per cui sarebbe 

f'{params_dir}/optimized_params_th_1_level_theta_baseline_vs_th_resp_std.txt'

**5)** al momento, il settaggio degli iper-parametri è impostato per anche per i casi multi-nomiali ma in questo caso il codice verrà usato per task di classificazione binaria...

per cui, voglio essere sicuro che l'impostazione attuale vada anche bene per i casi semplicemente binomiali, ossia di due possibili classi solo...

per farlo, ti do il link della pagina della Logistic Regression, in modo che tu mi dica se l'attuale implementazione sia corretta....

https://scikit-learn.org/1.5/modules/generated/sklearn.linear_model.LogisticRegression.html


**6)** Fai le modifiche a quello che ti ho chiesto, non azzardare cose in più od in meno, vorrei che ti attenessi a ciò che ti ho chiesto...


##### **IMPLEMENTATION XGBOOST FOR COUPLED EXPERIMENTAL CONDITIONS**

In [ ]:
new_subject_level_concatenations_coupled_exp_th['th_19']['theta']['baseline_vs_th_resp'].keys()

In [ ]:
''' XGBOOST --> TERAPISTI GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.

'''


# Prepare a series of classifier applied to 50 time samples window with 25 stride

#XGBoost
#To use xgb.XGBClassifier in your project, 
#you can refer to the XGBoost documentation. 
#XGBClassifier is a part of the XGBoost library, designed for classification tasks using gradient boosting.

'''
Yes, you can use XGBoost for multi-class classification. 

The xgb.XGBClassifier supports multi-class classification 
by setting the objective parameter to multi:softmax or multi:softprob. 

Here’s how you can set it up:
- multi:softmax: Sets the classifier to output the class with the highest predicted probability.
- multi:softprob: Sets the classifier to output the predicted probabilities of each class.

https://xgboost.readthedocs.io/en/stable/python/python_api.html#xgboost.XGBClassifier
'''

#Per trovare migliori iperametri per Xgboost

#Google Scholar: best hyperparametrs for xgboost classification
#https://scholar.google.com/scholar?hl=it&as_sdt=0%2C5&q=best+hyperparametrs+for+xgboost+classification&btnG=&oq=best+hyperparametrs+for+XGBoost+classi

#https://arxiv.org/pdf/1901.08433
#https://dl.acm.org/doi/abs/10.1145/3297067.3297080


import numpy as np
import time
import torch

from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler

from xgboost import XGBClassifier

import joblib
import json
import os



param_distributions = {
    "learning_rate": [float(x) for x in (np.arange(0.005, 0.301, 0.05))],  # Da 0.005 a 0.3 con passo 0.05
    "subsample": [float(x) for x in (np.arange(0.8, 1.05, 0.05))],        # Da 0.8 a 1 con passo 0.05
    "max_leaves": [int(x) for x in (np.arange(10, 51, 5))],             # Da 10 a 50 con passo 5
    "max_depth": [int(x) for x in (np.arange(5, 31, 5))],              # Da 5 a 30 con passo 5
    "gamma": [float(x) for x in (np.arange(0, 0.03, 0.005))],            # Da 0 a 0.03 con passo 0.005
    "colsample_bytree": [float(x) for x in (np.arange(0.8, 1.05, 0.05))], # Da 0.8 a 1 con passo 0.05
    "min_child_weight": [int(x)for x in (np.arange(1, 11, 1))]}       # Da 1 a 10 con passo 1



'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond"

# Iterazione sulla struttura `new_subject_level_concatenations_coupled_exp_th`

for subject, levels in new_subject_level_concatenations_coupled_exp_th.items():
    
    #if subject == 'th_16':
    #if subject == 'th_17' or subject == 'th_18' or subject == 'th_19':
    
    #if subject == 'th_20':
    print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")

    for level_key, experimental_condition in levels.items():

        # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
        #                                      'delta' = δ,i.e., approx_5 ,
        #                                      'theta_strict' = Θ, i.e., detail_5,
        #                                      'labels') 

        # Identificazione del livello
        if level_key == 'theta':
            level = "approx_4"


        elif level_key == 'delta':
            level = "approx_5"


        elif level_key == 'theta_strict':
            level = "detail_5"

        else:
            continue  # Ignora livelli non rilevanti


        print(f"\nProcessing Data \033[1m from Level: \033[1m{level_key}\033[0m for Subject \033[1m{subject}\033[0m")

        for condition, data_dict in experimental_condition.items():

            # Estrazione dei dati e delle label
            X = data_dict['data'] # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente

            # Messaggi di log per dati e label
            print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

            print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

            y = data_dict['labels'] # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente


            '''NEW VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            params_dir = params_dir

            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f"{params_dir}/optimized_params_{subject}_level_{level}_{condition}_std.txt"

            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")
            print(f"\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE XGBOOST

            base_clf = XGBClassifier(objective = 'binary:logistic', use_label_encoder = False, eval_metric = 'logloss')

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            #invalid_combination_count = 0

            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")


                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_clf,
                        param_distributions = param_distributions,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:

                        for i, params in enumerate(rand_search.cv_results_['params']):


                            #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                            #calcolato sulla base di una cross-validation a 5 fold. 
                            #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                            #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                            #In sintesi, è il valore medio di accuracy ottenuto 
                            #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                            #per una specifica combinazione di iper-parametri!


                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                invalid_combination_count += 1
                                print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri

                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH

                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")            

##### **ALL SINGLE Therapists (TH01-TH16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **EEG preprocessed signal**: filtered 1-20

In [ ]:
#new_subject_level_concatenations_pt_1_20.keys()
#new_subject_level_concatenations_pt_1_20['pt_1'].keys()

#new_subject_level_concatenations_coupled_exp_pt.keys()

#new_subject_level_concatenations_coupled_exp_pt_1_20.keys()
#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1'].keys()


#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp'].keys()

In [ ]:
!pwd

In [ ]:
cd ..


In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import pickle
import numpy as np


with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th_1_20 = pickle.load(f)

In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun livello temporale (th_1, th_2, ..., th_16)
for id_subj in new_subject_level_concatenations_coupled_exp_th_1_20.keys():
    
    # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
    for exp_cond in new_subject_level_concatenations_coupled_exp_th_1_20[id_subj].keys():
        
        # Verifica che 'data' sia presente tra le chiavi della condizione
        if 'data' in new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]:
            
            # Estrai i dati originali
            dati_originali = new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]['data']
            
            # Sotto-seleziona i canali di interesse
            dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali
            
            # Aggiorna la chiave 'data' con i dati filtrati
            new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]['data'] = dati_sottoselezionati

            # Opzionale: stampa di controllo per verificare la nuova forma dei dati
            print(f"Subj \033[1m{id_subj}\033[0m, Condizione \033[1m{exp_cond}\033[0m: {dati_sottoselezionati.shape}")

In [ ]:
new_subject_level_concatenations_coupled_exp_th_1_20.keys()
np.shape(new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp']['data'])

In [ ]:
''' XGBOOST --> TERAPISTI GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.

'''


# Prepare a series of classifier applied to 50 time samples window with 25 stride

#XGBoost
#To use xgb.XGBClassifier in your project, 
#you can refer to the XGBoost documentation. 
#XGBClassifier is a part of the XGBoost library, designed for classification tasks using gradient boosting.

'''
Yes, you can use XGBoost for multi-class classification. 

The xgb.XGBClassifier supports multi-class classification 
by setting the objective parameter to multi:softmax or multi:softprob. 

Here’s how you can set it up:
- multi:softmax: Sets the classifier to output the class with the highest predicted probability.
- multi:softprob: Sets the classifier to output the predicted probabilities of each class.

https://xgboost.readthedocs.io/en/stable/python/python_api.html#xgboost.XGBClassifier
'''

#Per trovare migliori iperametri per Xgboost

#Google Scholar: best hyperparametrs for xgboost classification
#https://scholar.google.com/scholar?hl=it&as_sdt=0%2C5&q=best+hyperparametrs+for+xgboost+classification&btnG=&oq=best+hyperparametrs+for+XGBoost+classi

#https://arxiv.org/pdf/1901.08433
#https://dl.acm.org/doi/abs/10.1145/3297067.3297080


import numpy as np
import time
import torch

from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler

from xgboost import XGBClassifier

import joblib
import json
import os



param_distributions = {
    "learning_rate": [float(x) for x in (np.arange(0.005, 0.301, 0.05))],  # Da 0.005 a 0.3 con passo 0.05
    "subsample": [float(x) for x in (np.arange(0.8, 1.05, 0.05))],        # Da 0.8 a 1 con passo 0.05
    "max_leaves": [int(x) for x in (np.arange(10, 51, 5))],             # Da 10 a 50 con passo 5
    "max_depth": [int(x) for x in (np.arange(5, 31, 5))],              # Da 5 a 30 con passo 5
    "gamma": [float(x) for x in (np.arange(0, 0.03, 0.005))],            # Da 0 a 0.03 con passo 0.005
    "colsample_bytree": [float(x) for x in (np.arange(0.8, 1.05, 0.05))], # Da 0.8 a 1 con passo 0.05
    "min_child_weight": [int(x)for x in (np.arange(1, 11, 1))]}       # Da 1 a 10 con passo 1


'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond_1_20"



for idx_subj, subject_data in new_subject_level_concatenations_coupled_exp_th_1_20.items():
    
    level_str = 'filtered_1_20'
    
    #if idx_subj == 'th_1':
    #if idx_subj == 'th_17' or idx_subj == 'th_18' or idx_subj == 'th_19':   
    if idx_subj == 'th_20':
        
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {idx_subj}\033[0m\n\n")

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        #for condition in new_subject_level_concatenations_coupled_exp_th_1_20[idx_subj].keys():

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        for condition, condition_data in subject_data.items():

            #print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Creazione stringa per salvataggio files ('filtered_1_20')
            #level_str == 'filtered_1_20'

            print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente
            #X = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['data']

            # Estrazione dei dati e delle etichette
            X = condition_data['data']


            # Messaggi di log per dati e label
            print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente
            #y = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['labels'] 

            y = condition_data['labels']

            print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            '''NEW VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            params_dir = params_dir

            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f"{params_dir}/optimized_params_{idx_subj}_level_{level_str}_{condition}_std.txt"

            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{idx_subj}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")

            print(f"\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}

            #INIZIALIZZAZIONE XGBOOST

            base_clf = XGBClassifier (objective = 'binary:logistic', use_label_encoder = False, eval_metric = 'logloss')

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0

            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")


                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_clf,
                        param_distributions = param_distributions,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:

                        for i, params in enumerate(rand_search.cv_results_['params']):


                            #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                            #calcolato sulla base di una cross-validation a 5 fold. 
                            #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                            #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                            #In sintesi, è il valore medio di accuracy ottenuto 
                            #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                            #per una specifica combinazione di iper-parametri!


                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                invalid_combination_count += 1
                                #print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri

                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH

                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")            


#### **ALL SINGLE Therapists (TH01-TH20)**

#### Plots of **EACH SINGLE Subject's Accuracy Score Performances** 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**


##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 - OLD VERSION**

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI**


In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_th = {}
    best_scores_level_5_single_th = {}
    best_scores_level_5_detail_th = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "all_th_level_4_std" in file_name or "all_th_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            #if level == 4 and subject not in best_scores_level_4_single_th:
            if level == 'approx_4' and subject not in best_scores_level_4_single_th:    
                best_scores_level_4_single_th[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_th:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_th:
                best_scores_level_5_single_th[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_th:
                best_scores_level_5_detail_th[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_th[subject][window] = max(best_scores_level_4_single_th[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_th[subject][window] = max(best_scores_level_5_single_th[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_th[subject][window] = max(best_scores_level_5_detail_th[subject][window], best_score)

    return best_scores_level_4_single_th, best_scores_level_5_single_th, best_scores_level_5_detail_th  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_th_xgb, best_scores_level_5_single_th_xgb, best_scores_level_5_detail_th_xgb = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_th_xgb keys\033[0m: {best_scores_level_4_single_th_xgb.keys()}")

for th_key, window_key in best_scores_level_4_single_th_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_th_xgb keys\033[0m: {best_scores_level_5_single_th_xgb.keys()}")

for th_key, window_key in best_scores_level_5_single_th_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_th_xgb keys\033[0m: {best_scores_level_5_detail_th_xgb.keys()}")

for th_key, window_key in best_scores_level_5_detail_th_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
#pwd
#cd ..
#cd New_Plots_Sliding_Estimator_MNE

#path corretta --> cd Plots_Sliding_Estimator_MNE
#path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"

#Comandi da eseguire

#!pwd
#cd Plots_Sliding_Estimator_MNE


import pickle

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_level_4_single_th_xgb.pkl', 'wb') as file:
    pickle.dump(best_scores_level_4_single_th_xgb, file)
    
# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_level_5_single_th_xgb.pkl', 'wb') as file:
    pickle.dump(best_scores_level_5_single_th_xgb, file)

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_level_5_detail_th_xgb.pkl', 'wb') as file:
    pickle.dump(best_scores_level_5_detail_th_xgb, file)

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER EEG 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_th = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_th:    
                best_scores_filtered_1_20_single_th[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_th[subject][window] = max(best_scores_filtered_1_20_single_th[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_th

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_th_xgb = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_th_xgb keys\033[0m: {best_scores_filtered_1_20_single_th_xgb.keys()}")

for th_key, window_key in best_scores_filtered_1_20_single_th_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
!pwd

In [ ]:
#cd Interrogait/

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
#pwd
#cd ..
#cd New_Plots_Sliding_Estimator_MNE

#path corretta --> cd Plots_Sliding_Estimator_MNE
#path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"

#Comandi da eseguire

#!pwd
#cd Plots_Sliding_Estimator_MNE


import pickle

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_filtered_1_20_single_th_xgb.pkl', 'wb') as file:
    pickle.dump(best_scores_filtered_1_20_single_th_xgb, file)

#print("Dati concantenati dei Singoli Terapisti salvati in 'subject_level_concatenations_th_1_20.pkl'")


##### **ALL SINGLE Therapists (TH01-TH20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DALLE RICOSTRUZIONI - OLD VERSION**

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 APPROX & LEVEL 5 DETAIL DELLE RICOSTRUZIONI**

In [ ]:
pwd

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO TERAPISTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI APPROX 4, APPROX 5 e DETAIL 5

best_scores_level_4_single_th_xgb, 
best_scores_level_5_single_th_xgb,
best_scores_level_5_detail_th_xgb
'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
    # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    ths_baseline_accuracy_highest_class_in_fold_xgb = list()
    
    for subject, scores in best_scores_dict.items():
        
        '''Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_th:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_th[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            ths_baseline_accuracy_highest_class_in_fold_xgb.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        

        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'approx_4':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta'
            clf_str = 'xgb'
            
        elif level == 'approx_5':
            
            ax1.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            
            level_str = 'delta'
            clf_str = 'xgb'
                
                
        elif level == 'detail_5':
            
            ax1.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta_strict'
            clf_str = 'xgb'
            
        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='purple', zorder=5, label=f'Best Score XGboost for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='purple', zorder=5, label=f'Best Score XGBoost for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return ths_baseline_accuracy_highest_class_in_fold_xgb

# Esempio di utilizzo
save_path_level_4 = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5 = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5_detail = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
ths_baseline_accuracy_highest_class_in_fold_level_4_xgb = plot_best_scores_for_subjects(best_scores_level_4_single_th_xgb, 'approx_4', save_path_level_4)
ths_baseline_accuracy_highest_class_in_fold_level_5_xgb = plot_best_scores_for_subjects(best_scores_level_5_single_th_xgb, 'approx_5', save_path_level_5)
ths_baseline_accuracy_highest_class_in_fold_level_5_detail_xgb = plot_best_scores_for_subjects(best_scores_level_5_detail_th_xgb, 'detail_5', save_path_level_5)

In [ ]:
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl


# Salvare l'intero dizionario annidato con pickle
import pickle

with open('best_scores_level_4_single_th_xgb.pkl', 'wb') as f:
    pickle.dump(best_scores_level_4_single_th_xgb, f)

with open('best_scores_level_5_single_th_xgb.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_single_th_xgb, f)
    

with open('best_scores_level_5_detail_th_xgb.pkl', 'wb') as f:    
    pickle.dump(best_scores_level_5_detail_th_xgb, f)
#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('ths_baseline_accuracy_highest_class_in_fold_xgb.pkl', 'wb') as f:
#    pickle.dump(ths_baseline_accuracy_highest_class_in_fold_xgb, f)
    

#import pickle 
# Caricare il dizionario salvato con pickle
#with open('/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations_th.pkl', 'rb') as f:
#   subject_level_concatenations_th = pickle.load(f)

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
pwd

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)

In [ ]:
#new_subject_level_concatenations_th_1_20.keys()
#dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16'])

#new_subject_level_concatenations_th_1_20['th_16'].keys()
#dict_keys(['data', 'labels'])

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO TERAPISTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI FILTERED 1-20Hz

best_scores_filtered_1_20_single_th_xgb

'''


import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
    # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots_1_20')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    ths_baseline_accuracy_highest_class_in_fold_xgb = list()
    
    for subject, scores in best_scores_dict.items():
        
        ''' Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}_filtered_1_20')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_th_1_20:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_th_1_20[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            ths_baseline_accuracy_highest_class_in_fold_xgb.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        
        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'filtered_1_20':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)',  fontsize = 16)
            
            level_str = 'filtered_1_20'
            clf_str = 'xgb'
            

        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus Period (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='purple', zorder=5, label=f'Best Score XGBoost for {subject} for $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='purple', zorder=5, label=f'Best Score XGBoost for {subject} for $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return ths_baseline_accuracy_highest_class_in_fold_xgb

# Esempio di utilizzo
save_path_filtered_1_20 = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
ths_baseline_accuracy_highest_class_in_fold_1_20_xgb = plot_best_scores_for_subjects(best_scores_filtered_1_20_single_th_xgb, 'filtered_1_20', save_path_filtered_1_20)

#### **All Therapists (TH01-TH20)**

#### Plots of **Grand Average Mean** of Best Single Subject's Accuracy Score Performances 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **Istruzioni per il codice**

Fammi un codice python che faccia queste cose 

- **1)** Entrami in una **folder path** (che ti fornisco io) ed iteri in quella folder path
- **2)** Vedi se c'è in quella folder path ci siano dei **file che finiscono con .txt**: 

- **3)** Se vedi la porzione finale del file contiene la stringa 
    **"all_th_level_4_std"** o 
    **all_th_level_5_std"**

   e se incontri queste stringhe, **escludi quei file .txt** e continua.. 

- **4)** Vedi invece se la porzione finale del file contiene la stringa **"_level_4_std"** o **"_level_5_std**:

- - **4.1.)** In quel caso, entri dentro quel file e **leggilo** ma poi fai una ulteriore considerazione, ossia
  - - vedi se quello che precede "_level_4_std" o "_level_5_std" sia **" th_"** dove * è un **suffisso dinamico**, che va da
      1 a 15...

Quindi avrai per ogni soggetto, due file .txt, che finiranno con questa stringa 

Per il **soggetto 1**: "**th_1_level_4_std**" o "**th_1_level_5_std**" 
Per il **soggetto 2**: "**th_2_level_4_std**" o "**th_2_level_5_std**" 

E così via, fino al 15° soggetto...

- **5)** Vedi in ognuna delle coppie di file .txt dello stesso soggetto
 
(i.e., ossia per esempio avrai per il soggetto 1 due file .txt, che finiranno con questa stringa 

"th_1_level_4_std" o "th_1_level_5_std" )

- **7)** Leggi il file .txt e vedi se ci sia un **riga in quel file .txt** con scritto 

**"Best Score for Window"**, seguito da **una sequenza di stringhe dinamica**, che cambia e che può essere presa da una lista di stringhe iterativamente che si costruisce a priori, del tipo:

"0-50" "25-75" etc., ossia che cambia di 25 valori ogni volta in maniera uniforme, quindi proseguendo sarebbe:
"50-100" "75-125" "100-150" "125-175" "150-200" "175-225" "200-250" "225-275" "250-300"

Quindi la lista di stringa dinamica potrebbe essere

**n_windows** = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"]

di conseguenza, itera per ogni elemento di questa lista "n_windows" per riconoscere se questa **sequenza di stringa dinamica** completi un riga dentro il file .txt che avrà scritto quindi:
 
**"Best Score for Window" + {elemento della lista "n_windows}**:"

A questo punto, avrai l'intera riga che sarà ad esempio:

"Best Score for Window 0-50: ".. 

In quella stessa riga del file .txt, dovresti trovare un **valore float**.. 

- **8)** Vorrei che prendessi quel valore float e **lo appendessi ad un dizionario**, che conterrà nei suoi vari valori i vari **best score ottenuti da quel soggetto lì, per ciascuna delle finestra considerate**
(che vanno da 0-50 a 250-300, ossia prendendo a riferimento quello che c'è dentro "n_windows"

'n_windows = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"])

Questo dizionario la chiamerò ad esempio **"best_scores_level_4_single_th"**, che ad esempio avrà, 

come primo "valore", la chiave associata al primo soggetto (i.e, **th_1**)

il quale poi avrà 

- - **A)** come sotto-chiave il nome dell'elemento iterato rispetto a "n_windows" e 
- - **B)** come sotto-valore il valore float associato al best score trovato per quella finestra lì, per quel soggetto lì, del tipo

**th_1** =  {'**0-50**': valore float del best score ottenuto dal soggetto 1 sulla finestra 0-50,  
'25-75': valore float del best score ottenuto dal soggetto 1 sulla finestra 25-75... etc] 

quindi in sostanza, "**best_scores_level_4_single_th**" sarà un **dizionario annidato**, 

che conterrà altri dizionari, ognuno con il nome del soggetto e 
come sotto-chiave del sottodizionario il valore stringa di quella finestra, 
come sotto-valore, il valore di best score ottenuto da quel soggetto lì, per quella finestra testata, ognuno dopo l'altro ...

Infatti, percorrendo tutto il file .txt, avrai altre righe in cui potrebbe comparire questa sequenza di stringhe del tipo 

"Best Score for Window {elemento di n_windows} ".. 

Quindi, alla fine, creerò un numero di dizionari pari al numero di soggetti, ossia 

**th_1**
**th_2**
**th_3**
**th_4**
**th_5**
**th_6**
**th_7**
**th_8**
**th_9**
**th_10**
**th_11**
**th_12**
**th_13**
**th_14**
**th_15**

dove ciascuna conterrà il numero di finestre per cui ho calcolato il best score, che sarà diversa per ogni finestra ovviamente...

quindi del tipo avrò questa costruzione di questi dizionari:

**0-50**: 0.2681818181818182
**25-75**: 0.2681818181818182
**50-100**: 0.2681818181818182
**75-125**: 0.2621212121212121
**100-150**: 0.2621212121212121
**125-175**: 0.2621212121212121
**150-200**: 0.2621212121212121
**175-225**: 0.2621212121212121
**200-250**: 0.2681818181818182
**225-275**: 0.2621212121212121
**250-300**: 0.2621212121212121

ognuna, quindi, dovrà conteggiare 

i best score ottenuti da ogni singolo soggetto, 
per quella finestra di segnale EEG, 
per il livello di ricostruzione considerato 

(che è identificato dall'aver visto se la porzione finale della stringa associata al nome del file contenga la stringa "_level_4_std" o "_level_5_std, quando iteri dentro la folder path)...


<br>

La stessa sequenza di passaggi vorrei che venisse eseguita quando si controlla che la porzione finale della stringa associata al nome del file contenga la stringa "_level_5_std" ...

quindi in quel caso creerò dizionario **best_scores_level_4_single_th**, con dentro una stessa struttura ossia


th_1
th_2
th_3
th_4
th_5
th_6
th_7
th_8
th_9
th_10
th_11
th_12
th_13
th_14
th_15


ognuna con dentro 


0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121




<br>

Quindi che nel codice voglio che si prenda dal relativo file .txt del soggetto 

(per i due livelli di ricostruzione del segnale, ossia ad esempio dal primo soggetto 

"optimized_params_th_1_level_4_std.txt"
e 
"optimized_params_th_1_level_5_std.txt"

per ogni finestra considerata
(i.e., n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"])

il migliore best score che il soggetto 1 ha ottenuto quella finestra lì, ossia per la prima che sarà 0-50
e così via per le altre...

e che la stessa cosa la deve fare per ogni soggetto (th_2, th_3 etc.)


<br>
<br>
<br>


**N.B. INTEGRAZIONE AGGIUNTIVA PER ANALISI DI MEDIA GLOBALE!** 

Inoltre, quello che vorrei fare io è 

1) Per **ogni soggetto**, segnarmi
  - 1.1) il **valore di best score** per quella **specifica finestra** là,
  - 1.2) la **media dei punteggi** ottenuti in quella **specifica finestra** là .
  - 1.3.) la **relativa deviazione standard** di quel best score, **rispetto a quella finestra di quel soggetto specifico**..


Perché forse così ottengo una indicazione migliore di quanto è attendibile quel punteggio per quella finestra là, per quel soggetto lì... ma solo per quel soggetto lì, ossia srebbe una deviazione standard di quella finestra, ma soggetto-specifica... giusto?


Ossia, voglio ottenere una **misura di attendibilità specifica per ogni soggetto**. 

Quindi, stai cercando di **calcolare la deviazione standard dei punteggi di best score ottenuti per ciascuna finestra di un soggetto specifico**, tra tutte le combinazioni di iper-parametri testate. 

Questo darà **un'idea di quanto varia il miglior punteggio ottenuto per quella finestra per quel soggetto**.


STEPS :

- Estrai i punteggi migliori per ogni finestra e soggetto: Raccogli i punteggi migliori ottenuti per ciascuna finestra da tutte le combinazioni testate per quel soggetto.

- Calcola la deviazione standard per ciascuna finestra e soggetto: Per ogni finestra e soggetto, calcola la deviazione standard dei punteggi migliori ottenuti dai diversi modelli. Questo ti darà una misura di quanto varia il miglior punteggio ottenuto per quella finestra.


**OBIETTIVO**

La relazione che ti interessa è 

**come il best score si confronta con la deviazione standard rispetto al punteggio medio nella finestra. 
In altre parole, vuoi capire se il best score è significativamente alto rispetto alla variabilità (deviazione standard) dei punteggi in quella finestra**





**match = re.search(rf"{pattern}\s+([0-9]** * **\.?[0-9]+)",line)**


Serve per cercare all'interno di una stringa (line) un pattern specifico e, se trovato, estrae un numero in formato float dalla stringa.

<br>

**Dettagli della riga**:

- **re.search()**: Questa funzione di Python appartiene al modulo re, che si usa per eseguire operazioni con espressioni regolari (regex). La funzione cerca una corrispondenza all'interno di una stringa. Se trova una corrispondenza, restituisce un oggetto Match; altrimenti, restituisce None.

rf"{pattern}\s+([0-9]*\.?[0-9]+)": Questa è un'espressione regolare, ed è composta da diverse parti:

- **rf**: Significa "raw formatted string". Il prefisso r indica una "raw string", che dice a Python di non interpretare caratteri speciali come \ ma di passarli direttamente all'espressione regolare. Il prefisso f permette di inserire variabili nella stringa usando le parentesi graffe {}.

- **{pattern}**: È una variabile che contiene una stringa (in questo caso f"Best Score for Window {window}:"). Quindi, per esempio, potrebbe diventare "Best Score for Window 0-50:".
\s+: Questo significa "uno o più spazi bianchi" (spazi, tab, ecc.). Indica che dopo il pattern può esserci uno o più spazi prima del numero.

- **([0-9]*\.?[0-9]+)**: Questo è il pattern che identifica un numero in formato float.

<br>

Vediamolo in dettaglio:

- [0-9]*: cerca zero o più cifre (quindi permette che il numero inizi senza zeri).
\.?: cerca un punto decimale opzionale (il punto . è un carattere speciale nelle regex, quindi va preceduto da un backslash \).
- [0-9]+: cerca una o più cifre dopo il punto decimale (se presente).
- 
Complessivamente, questo pattern cerca un numero che può essere intero o decimale.

- **line**: È la stringa (riga di testo) in cui viene cercato il pattern. Nel tuo caso, line rappresenta ogni riga del file .txt che viene processata.

**Risultato (match)**: Se l'espressione regolare trova una corrispondenza (ovvero, se esiste una riga che contiene la stringa "Best Score for Window X-Y:" seguita da un numero float), re.search() restituisce un oggetto Match che contiene le informazioni della corrispondenza. Se non trova nulla, restituisce None.

<br>

**Esempio pratico**:
Supponiamo che pattern sia "Best Score for Window 0-50:" e che line contenga la seguente stringa:


"Best Score for Window 0-50: 0.85"

L'espressione regolare cercherà:

- "Best Score for Window 0-50:" (contenuto in pattern),
- poi uno o più spazi bianchi (\s+),
- e infine un numero float (([0-9]*\.?[0-9]+)), in questo caso 0.85.

Se viene trovata una corrispondenza, l'oggetto Match conterrà il numero 0.85.

Quindi, match.group(1) restituirà il numero 0.85 come stringa, che poi viene convertito in float

Ora vorrei che **per ogni dizionario**, per **ogni elemento di ogni dizionario** (ogni lista), vorrei che 

- mi calcolassi **la media** e la **deviazione standard** e
- me le **salvassi come ulteriori chiavi di quel dizionario lì**, col nome di chiave relativo alla lista da cui stai prendendo i valori float.

<br>

Esempio pratico:

Dalla chiave **"0-50"** calcolerai 
- la media
- la deviazione standard di quei valori lì

- E poi la media e la media e deviazione standard **li salvi dentro altre due
chiavi**:
  - una che si chiamerà **"mean_0-50_level_4**"
  - l'altra **"std_0-50_level_4"**


E così via **per tutte le altre finestre**, e **per entrambi i dizionari**, ossia 
- sia per **"all_th_best_scores_level_4"**
- sia per **"all_th_best_scores_level_5"**..

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **NEW VERSION**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_th = {}
    best_scores_level_5_single_th = {}
    best_scores_level_5_detail_th = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "all_th_level_4_std" in file_name or "all_th_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            #if level == 4 and subject not in best_scores_level_4_single_th:
            
            if level == 'approx_4' and subject not in best_scores_level_4_single_th:    
                best_scores_level_4_single_th[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_th:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_th:
                best_scores_level_5_single_th[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_th:
                best_scores_level_5_detail_th[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_th[subject][window] = max(best_scores_level_4_single_th[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_th[subject][window] = max(best_scores_level_5_single_th[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_th[subject][window] = max(best_scores_level_5_detail_th[subject][window], best_score)

    return best_scores_level_4_single_th, best_scores_level_5_single_th, best_scores_level_5_detail_th  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_th_xgb, best_scores_level_5_single_th_xgb, best_scores_level_5_detail_th_xgb = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_th_xgb keys\033[0m: {best_scores_level_4_single_th_xgb.keys()}")

for th_key, window_key in best_scores_level_4_single_th_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_th_xgb keys\033[0m: {best_scores_level_5_single_th_xgb.keys()}")

for th_key, window_key in best_scores_level_5_single_th_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_th_xgb keys\033[0m: {best_scores_level_5_detail_th_xgb.keys()}")

for th_key, window_key in best_scores_level_5_detail_th_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        '''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")
        
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_4 = calculate_mean_and_confidence_interval(best_scores_level_4_single_th_xgb, n_windows)
statistics_level_5 = calculate_mean_and_confidence_interval(best_scores_level_5_single_th_xgb, n_windows)
statistics_level_5_detail = calculate_mean_and_confidence_interval(best_scores_level_5_detail_th_xgb, n_windows)

In [ ]:
'''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
#print(best_scores_level_4_single_th_xgb['th_1']['0-50'])
#print(best_scores_level_4_single_th_xgb['th_2']['0-50'])
#print(best_scores_level_4_single_th_xgb['th_3']['0-50'])
#print()
#print(best_scores_level_4_single_th_xgb['th_1']['25-75'])
#print(best_scores_level_4_single_th_xgb['th_2']['25-75'])
#print(best_scores_level_4_single_th_xgb['th_3']['25-75'])


In [ ]:
type(statistics_level_4)

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
!pwd

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('new_all_th_concat_reconstructions.pkl', 'rb') as f:
    new_all_th_concat_reconstructions = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_th['th_1'].keys()

In [ ]:
new_all_th_concat_reconstructions.keys()

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME '''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    subjects_dir = os.path.join(save_path, f'plot_mean_all_ths_level_{level}')
    os.makedirs(subjects_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 4:
        level_str = 'theta'
    elif level == 5:
        level_str = 'delta'
    elif level == '5_detail':
        level_str = 'theta_strict'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'all_ths_level_{level_str}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    print(f"\n\t\t\t\t\t\033[1mTherapists'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_th_concat_reconstructions.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    
    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)

    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Aggiunge il livello di baseline in base al livello specificato
    #if level == 4:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range')
    #elif level == 5:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range')
    #elif level == '5_detail':
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Detail Range')
    
    '''VECCHIO'''
    
    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
    if level_str == 'theta':
        ax1.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range', fontsize = 16)
        ax2.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range',  fontsize = 16)
        
    elif level_str == 'delta':
        ax1.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)
        ax2.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)

    elif level_str == 'theta_strict':
        ax1.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
        ax2.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
    
    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='purple', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='purple', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_ths_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(subjects_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_4, 4, save_path)
plot_mean_best_scores_for_window(statistics_level_5, 5, save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail, '5_detail', save_path)

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE E PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    

 # Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_all_th_concat_reconstructions_1_20.pkl', 'rb') as f:
    new_all_th_concat_reconstructions_1_20 = pickle.load(f)

In [ ]:
print(new_subject_level_concatenations_th_1_20.keys())
print()
print(new_subject_level_concatenations_th_1_20['th_1'].keys())
print(new_subject_level_concatenations_th_1_20['th_1']['data'].shape)
print()
print(new_all_th_concat_reconstructions_1_20.keys())
print(new_all_th_concat_reconstructions_1_20['data'].shape)

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''

import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_th = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_th:    
                best_scores_filtered_1_20_single_th[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_th[subject][window] = max(best_scores_filtered_1_20_single_th[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_th

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_th_xgb = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_th_xgb keys\033[0m: {best_scores_filtered_1_20_single_th_xgb.keys()}")

for th_key, window_key in best_scores_filtered_1_20_single_th_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        '''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")
        
        
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc = mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_1_20 = calculate_mean_and_confidence_interval(best_scores_filtered_1_20_single_th_xgb, n_windows)

In [ ]:
'''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
#print(best_scores_filtered_1_20_single_th_xgb['th_1']['0-50'])
#print(best_scores_filtered_1_20_single_th_xgb['th_2']['0-50'])
#print(best_scores_filtered_1_20_single_th_xgb['th_3']['0-50'])
#print()
#print(best_scores_filtered_1_20_single_th_xgb['th_1']['25-75'])
#print(best_scores_filtered_1_20_single_th_xgb['th_2']['25-75'])
#print(best_scores_filtered_1_20_single_th_xgb['th_3']['25-75'])

In [ ]:
type(statistics_level_1_20)

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    data_dir = os.path.join(save_path, f'plot_mean_all_ths_level_{level}')
    os.makedirs(data_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 'filtered_1_20':
        level_str = 'filtered_1_20'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    #print(f"\n\t\t\t\t\t\033[1mPatients'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_th_concat_reconstructions_1_20.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}\n\n\n")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    
    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)
    
    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Linea orizzontale per il chance level
    #plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    #plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)')

    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è filtered_1_20, gestisci i titoli per i grafici su ax1 e ax2
    if level == 'filtered_1_20':

        ax1.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
        ax2.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)

    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='purple', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='purple', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='purple', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='purple', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_ths_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(data_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'\nPlot salvato in: \n\033[1m{save_file_path}\033[0m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_1_20, 'filtered_1_20', save_path)



#### **ALL SINGLE PATIENTS (PT01-PT20)**

#### Automatization of all steps from: 

1) "**subject_level_concatenations_pt**" : ricostruzioni 4 e 5° livello wavelet da approx coefficients
2) "**new_subject_level_concatenations_pt**":  ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_pt_1_20**": EEG preprocessed signal filtered 1-20Hz 

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)

##### **ALL SINGLE Patients (PT01-PT15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DALLE RICOSTRUZIONI**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**

In [ ]:
''' XGBOOST --> PAZIENTI! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.

'''


# Prepare a series of classifier applied to 50 time samples window with 25 stride

#XGBoost
#To use xgb.XGBClassifier in your project, 
#you can refer to the XGBoost documentation. 
#XGBClassifier is a part of the XGBoost library, designed for classification tasks using gradient boosting.

'''
Yes, you can use XGBoost for multi-class classification. 

The xgb.XGBClassifier supports multi-class classification 
by setting the objective parameter to multi:softmax or multi:softprob. 

Here’s how you can set it up:
- multi:softmax: Sets the classifier to output the class with the highest predicted probability.
- multi:softprob: Sets the classifier to output the predicted probabilities of each class.

https://xgboost.readthedocs.io/en/stable/python/python_api.html#xgboost.XGBClassifier
'''

#Per trovare migliori iperametri per Xgboost

#Google Scholar: best hyperparametrs for xgboost classification
#https://scholar.google.com/scholar?hl=it&as_sdt=0%2C5&q=best+hyperparametrs+for+xgboost+classification&btnG=&oq=best+hyperparametrs+for+XGBoost+classi

#https://arxiv.org/pdf/1901.08433
#https://dl.acm.org/doi/abs/10.1145/3297067.3297080


import numpy as np
import time
import torch

from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler

from xgboost import XGBClassifier

import joblib
import json
import os



param_distributions = {
    "learning_rate": [float(x) for x in (np.arange(0.005, 0.301, 0.05))],  # Da 0.005 a 0.3 con passo 0.05
    "subsample": [float(x) for x in (np.arange(0.8, 1.05, 0.05))],        # Da 0.8 a 1 con passo 0.05
    "max_leaves": [int(x) for x in (np.arange(10, 51, 5))],             # Da 10 a 50 con passo 5
    "max_depth": [int(x) for x in (np.arange(5, 31, 5))],              # Da 5 a 30 con passo 5
    "gamma": [float(x) for x in (np.arange(0, 0.03, 0.005))],            # Da 0 a 0.03 con passo 0.005
    "colsample_bytree": [float(x) for x in (np.arange(0.8, 1.05, 0.05))], # Da 0.8 a 1 con passo 0.05
    "min_child_weight": [int(x)for x in (np.arange(1, 11, 1))]}       # Da 1 a 10 con passo 1




# Itera attraverso i soggetti

'''OLD VERSION'''
#for subject, levels in subject_level_concatenations_th.items():


'''NEW VERSION'''

for subject, levels in new_subject_level_concatenations_pt.items():
    
    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO'''
    #if subject == 'pt_16':
    #if subject == 'pt_17' or subject == 'pt_18' or subject == 'pt_19':
    
    if subject == 'pt_20':
        
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")


        '''NEW VERSION'''
        #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
        params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params'

        # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
        #                                      'delta' = δ,i.e., approx_5 ,
        #                                      'theta_strict' = Θ, i.e., detail_5,
        #                                      'labels') 

        for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'


            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")

            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_std.txt'

            #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\t\033[1m{params_dir}\033[0m"),
            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

            y = levels['labels'] # Estraiamo le labels livello corrente del soggetto corrente


            #Path per combinazioni iperparametri NON valide
            #invalid_params_file_path = f'{params_dir}/invalid_params_{subject}_level_{level}_std.txt'

            print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE XGBOOST

            base_clf = XGBClassifier (objective = 'multi:softmax', use_label_encoder = False, eval_metric = 'logloss')

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            #invalid_combination_count = 0

            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")


                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_clf,
                        param_distributions = param_distributions,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:

                        for i, params in enumerate(rand_search.cv_results_['params']):


                            #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                            #calcolato sulla base di una cross-validation a 5 fold. 
                            #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                            #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                            #In sintesi, è il valore medio di accuracy ottenuto 
                            #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                            #per una specifica combinazione di iper-parametri!


                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                invalid_combination_count += 1
                                print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri

                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH

                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")            


##### **ALL SINGLE Patients (PT01-PT16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

- **EEG preprocessed signal**: filtered 1-20


In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun soggetto nel dizionario
for soggetto, dati in new_subject_level_concatenations_pt_1_20.items():
    
    # Verifica che 'data' sia presente tra le chiavi
    if 'data' in dati:
        
        # Sotto-seleziona i canali di interesse
        dati_originali = dati['data']  # Estrai i dati
        
        dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali

        # Aggiorna la chiave 'data' con i dati filtrati
        new_subject_level_concatenations_pt_1_20[soggetto]['data'] = dati_sottoselezionati

        # Opzionale: stampa di controllo per verificare la nuova forma dei dati
        print(f"Soggetto {soggetto}: {dati_sottoselezionati.shape}")

In [ ]:
##### **ALL SINGLE Patients (PT01-PT15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DAL SEGNALE 1-20Hz**


''' XGBOOST --> PAZIENTI GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.

'''


# Prepare a series of classifier applied to 50 time samples window with 25 stride

#XGBoost
#To use xgb.XGBClassifier in your project, 
#you can refer to the XGBoost documentation. 
#XGBClassifier is a part of the XGBoost library, designed for classification tasks using gradient boosting.

'''
Yes, you can use XGBoost for multi-class classification. 

The xgb.XGBClassifier supports multi-class classification 
by setting the objective parameter to multi:softmax or multi:softprob. 

Here’s how you can set it up:
- multi:softmax: Sets the classifier to output the class with the highest predicted probability.
- multi:softprob: Sets the classifier to output the predicted probabilities of each class.

https://xgboost.readthedocs.io/en/stable/python/python_api.html#xgboost.XGBClassifier
'''

#Per trovare migliori iperametri per Xgboost

#Google Scholar: best hyperparametrs for xgboost classification
#https://scholar.google.com/scholar?hl=it&as_sdt=0%2C5&q=best+hyperparametrs+for+xgboost+classification&btnG=&oq=best+hyperparametrs+for+XGBoost+classi

#https://arxiv.org/pdf/1901.08433
#https://dl.acm.org/doi/abs/10.1145/3297067.3297080


import numpy as np
import time
import torch

from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler

from xgboost import XGBClassifier

import joblib
import json
import os



param_distributions = {
    "learning_rate": [float(x) for x in (np.arange(0.005, 0.301, 0.05))],  # Da 0.005 a 0.3 con passo 0.05
    "subsample": [float(x) for x in (np.arange(0.8, 1.05, 0.05))],        # Da 0.8 a 1 con passo 0.05
    "max_leaves": [int(x) for x in (np.arange(10, 51, 5))],             # Da 10 a 50 con passo 5
    "max_depth": [int(x) for x in (np.arange(5, 31, 5))],              # Da 5 a 30 con passo 5
    "gamma": [float(x) for x in (np.arange(0, 0.03, 0.005))],            # Da 0 a 0.03 con passo 0.005
    "colsample_bytree": [float(x) for x in (np.arange(0.8, 1.05, 0.05))], # Da 0.8 a 1 con passo 0.05
    "min_child_weight": [int(x)for x in (np.arange(1, 11, 1))]}       # Da 1 a 10 con passo 1



# Itera attraverso i soggetti

#for subject, levels in subject_level_concatenations_pt_1_20.items():
for subject, subj_dict in new_subject_level_concatenations_pt_1_20.items():
    
    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO'''
    #if subject == 'pt_16':
    
    #if subject == 'pt_17' or subject == 'pt_18' or subject == 'pt_19':
    
    #if subject == 'pt_20':
        
    print(f"\n\nCurrent Subject \033[1m{subject}\033[0m")

    print(f"\n\n\033[1mExtraction of Data\033[0m from Subject \033[1m{subject}\033[0m from Original Filtered Signal in \033[1m1-20Hz\033[0m")

    X = subj_dict['data'] # Estraiamo i dati del soggetto corrente

    y = subj_dict['labels'] # Estraiamo le labels livello corrente del soggetto corrente

    #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
    params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20'

    #FILE PATH DINAMICA PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
    #A SECONDA DEL SOGGETTO E LIVELLO DI RICOSTRUZIONE DEI DATI PRESI IN ESAME 

    # Costruzione del percorso del file in maniera dinamica
    params_file_path = f'{params_dir}/optimized_params_{subject}_filtered_1_20_std.txt'


    if not os.path.exists(params_dir):
        os.makedirs(params_dir)

    #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\033[1m{params_dir}\033[0m"),
    #print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

    #Path per combinazioni iperparametri NON valide
    invalid_params_file_path = f'{params_dir}/invalid_params_{subject}_filtered_1_20_std.txt'

    print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

    y = y.astype(int) 

    print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


    # Calcola il numero totale di etichette livello 4/5°
    label_counts = np.unique(y, return_counts = True)[1]
    total_labels = len(y)

    # Calcola la percentuale di ciascuna classe
    class_proportions = label_counts / total_labels * 100

    print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

    # Calcola i pesi delle classi come l'inverso delle proporzioni
    class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

    # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
    class_weights /= class_weights.sum()

    print(f"\n\033[1mClass Weights {class_weights}\033[0m")

    # Crea un dizionario per class_weight
    class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


    '''INIZIALIZZAZIONE XGBOOST'''


    base_clf = XGBClassifier (objective = 'multi:softmax', use_label_encoder = False, eval_metric = 'logloss')

    # Memorizza il tempo di inizio
    start_time = time.time()

    # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
    execution_times = []

    # Contatori per combinazioni valide e non valide
    valid_combination_count = 0
    invalid_combination_count = 0

    # File di output per i parametri ottimizzati
    with open(params_file_path, 'w') as f:
        f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

    # File di output per i parametri ottimizzati NON validi
    with open(invalid_params_file_path, 'w') as invalid_f:
        invalid_f.write(f"Invalid Parameter Combinations\n\n")


    '''INIZIALIZZAZIONE RANDOM SEARCH'''

    # Lista per memorizzare i risultati delle finestre
    window_results = []

    # Creazione della finestra scorrevole con step e dimensioni desiderate
    n_samples = X.shape[2]
    window_size = 50
    step_size = 25
    n_windows = (n_samples - window_size) // step_size + 1


    #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

    # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

    for window_start in range(0, n_samples - window_size + 1, step_size):

        # Memorizza il tempo di inizio per il punto temporale corrente
        time_point_start = time.time()

        # Definiamo la finestra corrente
        window_end = window_start + window_size

        print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

        X_window = X[:, :, window_start:window_end]
        print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

        # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
        X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
        print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

        # Standardizza i dati della finestra corrente
        scaler = StandardScaler()
        X_window_standardized = scaler.fit_transform(X_window_reshaped)
        print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")


        try:
            print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


            rand_search = RandomizedSearchCV(
                estimator = base_clf,
                param_distributions = param_distributions,
                scoring ='accuracy',
                n_iter = 100,
                verbose = 1,
                n_jobs = -1
            )


            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

            # Esegui RandomizedSearchCV sulla finestra corrente
            rand_search.fit(X_window_standardized, y)


            # Controlla il numero totale di combinazioni testate
            total_combinations_tested = len(rand_search.cv_results_['params'])
            #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

            # Salva tutte le combinazioni testate per la finestra corrente
            with open(params_file_path, 'a') as f:

                for i, params in enumerate(rand_search.cv_results_['params']):

                    '''
                    Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                    calcolato sulla base di una cross-validation a 5 fold. 
                    Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                    fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                    In sintesi, è il valore medio di accuracy ottenuto 
                    mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                    per una specifica combinazione di iper-parametri!
                    '''

                    score = rand_search.cv_results_['mean_test_score'][i]
                    f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                for params in rand_search.cv_results_['params']:
                    if params:
                        valid_combination_count += 1
                    else:
                        invalid_combination_count += 1
                        print(f"Invalid combination found: {params}")

                #QUI

                # Ottieni il modello con i migliori iper-parametri

                best_model_params = rand_search.best_params_


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH

                best_score = rand_search.best_score_


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                # Memorizza i risultati della finestra corrente
                window_results.append({
                    'window_start': window_start,
                    'window_end': window_end,
                    'best_params': best_model_params,
                    'best_score': best_score
                })


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

            #Salva i parametri migliori per la finestra corrente in una riga del file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                f.write('\n')

        except Exception as e:

            print(f'Error: {e}')

            # Scrivi la combinazione non valida nel file di output
            with open(invalid_params_file_path, 'a') as invalid_f:
                invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
            continue


            # Memorizza il tempo di fine per il punto temporale corrente
            time_point_end = time.time()

            # Calcola il tempo di esecuzione per il punto temporale corrente
            time_point_elapsed = time_point_end - time_point_start

            # Aggiungi il tempo di esecuzione alla lista
            execution_times.append(time_point_elapsed)

            # Stampa i risultati per il punto temporale corrente
            #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
            #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
            #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
            #print()
            #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
            #print()

    # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

    # Definisci il range generale delle finestre che vuoi analizzare
    general_range = [0, 300]  # Puoi modificare il range se necessario

    # Filtra i risultati delle finestre nel range desiderato
    general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

    # Controlla se ci sono risultati validi all'interno del range specificato
    if general_results:

        # Trova la finestra con il punteggio migliore
        best_general_window = max(general_results, key=lambda x: x['best_score'])

        # Trova i parametri migliori per questa finestra specifica (se disponibili)
        best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
        best_general_window['best_params'] = best_params

        # Stampa le informazioni sulla finestra migliore trovata
        #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
        #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
        #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

    else:
        print("No valid windows found in the specified range.")


    # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
    window_results.append({
        'Best window_start': best_general_window['window_start'] if general_results else None,
        'Best window_end': best_general_window['window_end'] if general_results else None,
        'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
        'best_score': best_general_window['best_score'] if general_results else None
    })

    # Calcola il tempo di esecuzione totale
    end_time = time.time()
    total_execution_time = end_time - start_time

    #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
    #print()
    #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
    #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

    # Aggiungi il risultato della migliore finestra generale al file di testo
    with open(params_file_path, 'a') as f:
        f.write('\n')
        if general_results:
            best_general_window = max(general_results, key=lambda x: x['best_score'])
            f.write(f"BEST WINDOW OVERALL: "),
            f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
            f.write(f"\nBest Window End: {best_general_window['window_end']}"),
            f.write(f"\nBest Score: {best_general_window['best_score']}")

            if best_general_window['best_params'] is not None:
                    f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
            else:
                f.write("No valid windows found in the specified range.\n")

            f.write('\n')
            f.write(f"Total execution time: {total_execution_time} seconds\n")
            f.write(f"Number of valid combinations: {valid_combination_count}\n")
            f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")            

#### **ALL SINGLE Patients (PT01-PT20) for **COUPLED EXPERIMENTAL CONDITIONS****

#### Automatization of all steps from: 

1) "**new_subject_level_concatenations_coupled_exp_pt**" ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_coupled_exp_pt_1_20**": EEG preprocessed signal filtered 1-20Hz 

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''


#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
#    new_subject_level_concatenations_th = pickle.load(f)
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle
import numpy as np


with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt_1_20 = pickle.load(f)
    


    
    
#PER SALVARE I FILE
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('NOME DEL FILE.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations, f)


#subject_level_concatenations_th['th_1'].keys()

In [ ]:
print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_pt\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt['pt_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp'].keys()}")

In [ ]:
np.unique(new_subject_level_concatenations_coupled_exp_pt['pt_16']['theta']['baseline_vs_th_resp']['labels'],return_counts=True)

##### **Descrizione degli step nel codice per ottenere e salvare nelle paths le best score performances per il level 4 e 5 dalle ricostruzioni**:

Vorrei in questo caso, per velocizzare, iterare su 

subject_level_concatenations, che ha questa struttura...

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


al cui interno ha per ogni chiave di primo ordine, un altro dizionario annidato, che è fatto di queste chiavi


dict_keys(['theta', 'delta', 'labels'])

dentro 'theta' e 'delta' ci sono tutti i dati di tutte le condizioni sperimentali del singolo soggetto

del tipo 'theta' o 'delta' conterrà un array con shape

(204, 3, 300)

con 1° dimensione i trial, poi i canali, poi i punti di ogni trial (campioni EEG)

e dentro 'labels' ho invece l'array delle labels concatenate...
(204,)


<br>


Ora però, vorrei che ... 

Se ad esempio nel soggetto 'th_1' entri nella chiave 'theta', 

allora poi il file corrispondente .txt deve essere scritto con una path dinamica, che cambia a seconda 
- sia del soggetto iterato
- sia del livello di ricostruzione dei dati

Ossia:

la "params_dir" è fissa

mentre 

"params_file_path" è dinamica, e cambia a seconda del soggetto iterato e del livello. 

Per cui sarà una composizione di stringhe fisse e stringhe 'mobili', ossia

'params_file_path' = 'optimized_params_' + {subject} dove subject dovrebbe essere una lista di stringhe che si preleva dalle chiavi di primo ordine di "subject_level_concatenations" che erano

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


seguito da "_level_{level}_std" dove {level} dipende dal nome della chiave del sotto-dizionario iterato per ogni soggetto...

Ossia, ad esempio dentro il sotto-dizionario del primo soggetto di "subject_level_concatenations" cioè

subject_level_concatenations['th_1'], 

Se la sua sotto-chiave è 'theta' allora il level = 4, se la chiave è 'delta' allora il level = 5, 



Quindi la costruzione finale della path dinamica del file specifico per il soggetto 1 deve essere

 
params_file_path = 'optimized_params_' +'{subject}' + "_level_{level}_std.txt"

e sarà se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_1' + "_level_4_std.txt"


e sarà se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_1' + "_level_5_std.txt"


in questo modo, farei un loop unico su tutte le sottochiavi dei dizionari annidati dentro 
"subject_level_concatenations" 

ossia 
dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

e per ognuno vedo se la sua sotto-chiave sarà 'theta' o 'delta' e creerà dei file .txt corrispondenti nella param_dir che gli ho chiesto...

Il resto del codice non toccarlo invece, perché dovrebbe creare dei file .txt per ogni soggetto per ogni livello di ricostruzione dei dati,
e salverà le analisi nel file .txt corrispondente



Ad esempio, continuando col soggetto 2:

la costruzione finale della path dinamica del file specifico per il soggetto 2

Sarà, se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_2' + "_level_4_std.txt"


e sarà, se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_2' + "_level_5_std.txt"


e così via per tutti gli altri soggetti




##### **ALL SINGLE Patients (PT01-PT16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DALLE RICOSTRUZIONI** 

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**


###### **ISTRUZIONI PER MODIFICHE AL CASO 2 CLASSI**

Allora, andiamo per step:

**1)** la nuova variabile sulla quale iterare è new_subject_level_concatenations_coupled_exp_th

che è fatta con questa struttura

print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_th\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()}")

OUTPUT:

Dataset Organization: new_subject_level_concatenations_coupled_exp_th

First Order Key: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16'])

Second Order Key: dict_keys(['theta', 'delta', 'theta_strict'])

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

Fourth Order Key: dict_keys(['data', 'labels'])

quindi significa che, per ogni soggetto, tu dovrai entrare nella sotto sotto chiave relativa ai livelli di ricostruzione del segnale 

dict_keys(['theta', 'delta', 'theta_strict'])

per ognuna di queste, avrai appunto delle altre sotto-sotto-sotto chiavi, che sono le condizioni sperimentali, sulle quali dovrai entrare che sono 

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

dopodiché dentro ognuna di queste, dovrai entrare ulteriormente dentro ciascuna sotto chiave di quarto livello:

la prima, che fa riferimento ai dati('data') il cui valore (array numpy() verrà assegnato ad X nel codice, e 
la seconda, la chiave delle labels ('labels') il cui valore verrà assegnato ad Y...

**2)** questa parte relativa ai print

 for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'

voglio che poi abbia degli altri if, nel senso che vorrei che iterando su ogni livello, voglio che venga applicata la stessa logica dei printing di qui sopra, ma alle chiavi del 3° livello, ossia quelle che fanno riferimento alle condizioni sperimentali...

ossia, 

voglio che ci sia scritto per le X

print(f"\n\033[1mExtraction of Data\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

e voglio che ci sia scritto per le Y

print(f"\n\033[1mExtraction of Labels\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

dove 

"experimental_condition" farà riferimento alla chiave della condizione sperimentale iterata in quel loop, e 

"level_key" invece farà riferimento alle chiavi del 2° livello, ossia a quelle che si riferiscono allo specifico livello di ricostruzione del segnale per il quale io sto estraendo i dati e le labels al ciclo corrente...

In questo modo, dovrei avere un'idea dai print del mio codice, quando viene eseguito, su quale soggetto, quale livello e quale condizione sperimentale sta eseguendo i calcoli.. 

**3)** voglio che vengano create dei folder nuovi per appendere i risultati di tutte le elaborazioni da parte dei vari modelli e che saranno queste due cartelle

"EEG_50_window_25_overlap_coupled_exp_cond" 
"single_therapist_optimized_params_coupled_exp_cond"
 
ossia la mia directory dovrebbe diventare

params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond'

per cui, se "EEG_50_window_25_overlap_coupled_exp_cond" né "single_therapist_optimized_params_coupled_exp_cond" non sono state create, allora andranno create...

**4)** la creazione del nome del file relativo ad un determinato soggetto dovrà essere formato in questo modo

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

dove, ricorda, "experimental_condition" farà riferimento alle insieme delle stringhe che compongono la chiave della condizione sperimentale iterata in quel loop (chiavi di 3° livello di "new_subject_level_concatenations_coupled_exp_th" 

del tipo potrebbe essere

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

Con ad esempio:

subject = th_1
level = theta 
experimental_condition = baseline_vs_th_resp

per cui sarebbe 

f'{params_dir}/optimized_params_th_1_level_theta_baseline_vs_th_resp_std.txt'

**5)** al momento, il settaggio degli iper-parametri è impostato per anche per i casi multi-nomiali ma in questo caso il codice verrà usato per task di classificazione binaria...

per cui, voglio essere sicuro che l'impostazione attuale vada anche bene per i casi semplicemente binomiali, ossia di due possibili classi solo...

per farlo, ti do il link della pagina della Logistic Regression, in modo che tu mi dica se l'attuale implementazione sia corretta....

https://scikit-learn.org/1.5/modules/generated/sklearn.linear_model.LogisticRegression.html


**6)** Fai le modifiche a quello che ti ho chiesto, non azzardare cose in più od in meno, vorrei che ti attenessi a ciò che ti ho chiesto...


##### **IMPLEMENTATION XGBOOST FOR COUPLED EXPERIMENTAL CONDITIONS**

In [ ]:
new_subject_level_concatenations_coupled_exp_pt['pt_20']['theta']['baseline_vs_th_resp'].keys()

In [ ]:
''' XGBOOST --> TERAPISTI GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.

'''


# Prepare a series of classifier applied to 50 time samples window with 25 stride

#XGBoost
#To use xgb.XGBClassifier in your project, 
#you can refer to the XGBoost documentation. 
#XGBClassifier is a part of the XGBoost library, designed for classification tasks using gradient boosting.

'''
Yes, you can use XGBoost for multi-class classification. 

The xgb.XGBClassifier supports multi-class classification 
by setting the objective parameter to multi:softmax or multi:softprob. 

Here’s how you can set it up:
- multi:softmax: Sets the classifier to output the class with the highest predicted probability.
- multi:softprob: Sets the classifier to output the predicted probabilities of each class.

https://xgboost.readthedocs.io/en/stable/python/python_api.html#xgboost.XGBClassifier
'''

#Per trovare migliori iperametri per Xgboost

#Google Scholar: best hyperparametrs for xgboost classification
#https://scholar.google.com/scholar?hl=it&as_sdt=0%2C5&q=best+hyperparametrs+for+xgboost+classification&btnG=&oq=best+hyperparametrs+for+XGBoost+classi

#https://arxiv.org/pdf/1901.08433
#https://dl.acm.org/doi/abs/10.1145/3297067.3297080


import numpy as np
import time
import torch

from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler

from xgboost import XGBClassifier

import joblib
import json
import os



param_distributions = {
    "learning_rate": [float(x) for x in (np.arange(0.005, 0.301, 0.05))],  # Da 0.005 a 0.3 con passo 0.05
    "subsample": [float(x) for x in (np.arange(0.8, 1.05, 0.05))],        # Da 0.8 a 1 con passo 0.05
    "max_leaves": [int(x) for x in (np.arange(10, 51, 5))],             # Da 10 a 50 con passo 5
    "max_depth": [int(x) for x in (np.arange(5, 31, 5))],              # Da 5 a 30 con passo 5
    "gamma": [float(x) for x in (np.arange(0, 0.03, 0.005))],            # Da 0 a 0.03 con passo 0.005
    "colsample_bytree": [float(x) for x in (np.arange(0.8, 1.05, 0.05))], # Da 0.8 a 1 con passo 0.05
    "min_child_weight": [int(x)for x in (np.arange(1, 11, 1))]}       # Da 1 a 10 con passo 1



'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_patient_optimized_params_coupled_exp_cond"

# Iterazione sulla struttura `new_subject_level_concatenations_coupled_exp_pt`

for subject, levels in new_subject_level_concatenations_coupled_exp_pt.items():
    
    #if subject == 'th_1':
    #if subject == 'pt_17' or subject == 'pt_18' or subject == 'pt_19': 
    
    print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")

    for level_key, experimental_condition in levels.items():

        # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
        #                                      'delta' = δ,i.e., approx_5 ,
        #                                      'theta_strict' = Θ, i.e., detail_5,
        #                                      'labels') 

        # Identificazione del livello
        if level_key == 'theta':
            level = "approx_4"


        elif level_key == 'delta':
            level = "approx_5"


        elif level_key == 'theta_strict':
            level = "detail_5"

        else:
            continue  # Ignora livelli non rilevanti


        print(f"\nProcessing Data \033[1m from Level: \033[1m{level_key}\033[0m for Subject \033[1m{subject}\033[0m")

        for condition, data_dict in experimental_condition.items():

            # Estrazione dei dati e delle label
            X = data_dict['data'] # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente

            # Messaggi di log per dati e label
            print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

            print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

            y = data_dict['labels'] # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente


            '''NEW VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            params_dir = params_dir

            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f"{params_dir}/optimized_params_{subject}_level_{level}_{condition}_std.txt"

            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")
            print(f"\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE XGBOOST

            base_clf = XGBClassifier(objective = 'binary:logistic', use_label_encoder = False, eval_metric = 'logloss')

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0


            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")


                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_clf,
                        param_distributions = param_distributions,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:

                        for i, params in enumerate(rand_search.cv_results_['params']):


                            #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                            #calcolato sulla base di una cross-validation a 5 fold. 
                            #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                            #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                            #In sintesi, è il valore medio di accuracy ottenuto 
                            #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                            #per una specifica combinazione di iper-parametri!


                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                invalid_combination_count += 1
                                #print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri

                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH

                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")            



##### **ALL SINGLE Patients (PT01-PT16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **EEG preprocessed signal**: filtered 1-20

In [ ]:
#new_subject_level_concatenations_pt_1_20.keys()
#new_subject_level_concatenations_pt_1_20['pt_1'].keys()

#new_subject_level_concatenations_coupled_exp_pt.keys()

#new_subject_level_concatenations_coupled_exp_pt_1_20.keys()
#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1'].keys()


#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp'].keys()

In [ ]:
import pickle
import numpy as np


with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt_1_20 = pickle.load(f)

In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun livello temporale (th_1, th_2, ..., th_16)
for id_subj in new_subject_level_concatenations_coupled_exp_pt_1_20.keys():
    
    # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
    for exp_cond in new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj].keys():
        
        # Verifica che 'data' sia presente tra le chiavi della condizione
        if 'data' in new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj][exp_cond]:
            
            # Estrai i dati originali
            dati_originali = new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj][exp_cond]['data']
            
            # Sotto-seleziona i canali di interesse
            dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali
            
            # Aggiorna la chiave 'data' con i dati filtrati
            new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj][exp_cond]['data'] = dati_sottoselezionati

            # Opzionale: stampa di controllo per verificare la nuova forma dei dati
            print(f"Subj \033[1m{id_subj}\033[0m, Condizione \033[1m{exp_cond}\033[0m: {dati_sottoselezionati.shape}")

In [ ]:
new_subject_level_concatenations_coupled_exp_pt_1_20.keys()
np.shape(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp']['data'])

In [ ]:
''' XGBOOST --> TERAPISTI GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.

'''


# Prepare a series of classifier applied to 50 time samples window with 25 stride

#XGBoost
#To use xgb.XGBClassifier in your project, 
#you can refer to the XGBoost documentation. 
#XGBClassifier is a part of the XGBoost library, designed for classification tasks using gradient boosting.

'''
Yes, you can use XGBoost for multi-class classification. 

The xgb.XGBClassifier supports multi-class classification 
by setting the objective parameter to multi:softmax or multi:softprob. 

Here’s how you can set it up:
- multi:softmax: Sets the classifier to output the class with the highest predicted probability.
- multi:softprob: Sets the classifier to output the predicted probabilities of each class.

https://xgboost.readthedocs.io/en/stable/python/python_api.html#xgboost.XGBClassifier
'''

#Per trovare migliori iperametri per Xgboost

#Google Scholar: best hyperparametrs for xgboost classification
#https://scholar.google.com/scholar?hl=it&as_sdt=0%2C5&q=best+hyperparametrs+for+xgboost+classification&btnG=&oq=best+hyperparametrs+for+XGBoost+classi

#https://arxiv.org/pdf/1901.08433
#https://dl.acm.org/doi/abs/10.1145/3297067.3297080


import numpy as np
import time
import torch

from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler

from xgboost import XGBClassifier

import joblib
import json
import os



param_distributions = {
    "learning_rate": [float(x) for x in (np.arange(0.005, 0.301, 0.05))],  # Da 0.005 a 0.3 con passo 0.05
    "subsample": [float(x) for x in (np.arange(0.8, 1.05, 0.05))],        # Da 0.8 a 1 con passo 0.05
    "max_leaves": [int(x) for x in (np.arange(10, 51, 5))],             # Da 10 a 50 con passo 5
    "max_depth": [int(x) for x in (np.arange(5, 31, 5))],              # Da 5 a 30 con passo 5
    "gamma": [float(x) for x in (np.arange(0, 0.03, 0.005))],            # Da 0 a 0.03 con passo 0.005
    "colsample_bytree": [float(x) for x in (np.arange(0.8, 1.05, 0.05))], # Da 0.8 a 1 con passo 0.05
    "min_child_weight": [int(x)for x in (np.arange(1, 11, 1))]}       # Da 1 a 10 con passo 1


'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_patient_optimized_params_coupled_exp_cond_1_20"



for idx_subj, subject_data in new_subject_level_concatenations_coupled_exp_pt_1_20.items():
    
    level_str = 'filtered_1_20'
    
    #if id_subj == 'th_1':
    
    if idx_subj == 'pt_17' or idx_subj == 'pt_18' or idx_subj == 'pt_19': 
        
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {idx_subj}\033[0m\n\n")

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        #for condition in new_subject_level_concatenations_coupled_exp_th_1_20[idx_subj].keys():

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        for condition, condition_data in subject_data.items():

            #print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Creazione stringa per salvataggio files ('filtered_1_20')
            #level_str == 'filtered_1_20'

            print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente
            #X = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['data']

            # Estrazione dei dati e delle etichette
            X = condition_data['data']


            # Messaggi di log per dati e label
            print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente
            #y = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['labels'] 

            y = condition_data['labels']

            print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            '''NEW VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            params_dir = params_dir

            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f"{params_dir}/optimized_params_{idx_subj}_level_{level_str}_{condition}_std.txt"

            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{idx_subj}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")

            print(f"\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE XGBOOST

            base_clf = XGBClassifier (objective = 'binary:logistic', use_label_encoder = False, eval_metric = 'logloss')

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0

            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")


                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_clf,
                        param_distributions = param_distributions,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:

                        for i, params in enumerate(rand_search.cv_results_['params']):


                            #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                            #calcolato sulla base di una cross-validation a 5 fold. 
                            #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                            #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                            #In sintesi, è il valore medio di accuracy ottenuto 
                            #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                            #per una specifica combinazione di iper-parametri!


                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                invalid_combination_count += 1
                                #print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri

                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH

                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")            


#### **ALL SINGLE Patients (PT01-PT20)**

#### Plots of **EACH SINGLE Subject's Accuracy Score Performances** 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**


##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI - OLD VERSION**

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DALLE RICOSTRUZIONI**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_pt = {}
    best_scores_level_5_single_pt = {}
    best_scores_level_5_detail_pt = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_pt_level_4_std" o "all_th_level_5_std"
            if "all_pt_level_4_std" in file_name or "all_pt_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'pt_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            #if level == 4 and subject not in best_scores_level_4_single_pt:
            if level == 'approx_4' and subject not in best_scores_level_4_single_pt:    
                best_scores_level_4_single_pt[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_pt:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_pt:
                best_scores_level_5_single_pt[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_pt:
                best_scores_level_5_detail_pt[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_pt[subject][window] = max(best_scores_level_4_single_pt[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_pt[subject][window] = max(best_scores_level_5_single_pt[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_pt[subject][window] = max(best_scores_level_5_detail_pt[subject][window], best_score)

    return best_scores_level_4_single_pt, best_scores_level_5_single_pt, best_scores_level_5_detail_pt  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_pt_xgb, best_scores_level_5_single_pt_xgb, best_scores_level_5_detail_pt_xgb = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_pt_xgb keys\033[0m: {best_scores_level_4_single_pt_xgb.keys()}")

for pt_key, window_key in best_scores_level_4_single_pt_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_pt_xgb keys\033[0m: {best_scores_level_5_single_pt_xgb.keys()}")

for pt_key, window_key in best_scores_level_5_single_pt_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_pt_xgb keys\033[0m: {best_scores_level_5_detail_pt_xgb.keys()}")

for pt_key, window_key in best_scores_level_5_detail_pt_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
!pwd

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER EEG 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_pt = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_pt:    
                best_scores_filtered_1_20_single_pt[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_pt[subject][window] = max(best_scores_filtered_1_20_single_pt[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_pt

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_pt_xgb = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_pt_xgb keys\033[0m: {best_scores_filtered_1_20_single_pt_xgb.keys()}")

for th_key, window_key in best_scores_filtered_1_20_single_pt_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
#pwd
#cd ..
#cd New_Plots_Sliding_Estimator_MNE

#path corretta --> cd Plots_Sliding_Estimator_MNE
#path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"

#Comandi da eseguire

#!pwd
#cd Plots_Sliding_Estimator_MNE


import pickle

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_filtered_1_20_single_pt_xgb.pkl', 'wb') as file:
    pickle.dump(best_scores_filtered_1_20_single_pt_xgb, file)

#print("Dati concantenati dei Singoli Terapisti salvati in 'subject_level_concatenations_th_1_20.pkl'")

##### **ALL SINGLE Patients (PT01-PT20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI - OLD VERSION**

##### **ALL SINGLE Patients (PT01-PT20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 APPROX DA COEFF APPROX & LEVEL 5 DA COEFF DETAIL DELLE RICOSTRUZIONI**

In [ ]:
!pwd

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    
#subject_level_concatenations_th.keys()

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO PAZIENTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI APPROX 4, APPROX 5 e DETAIL 5

best_scores_level_4_single_pt_xgb, 
best_scores_level_5_single_pt_xgb,
best_scores_level_5_detail_pt_xgbin
'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
     # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    pts_baseline_accuracy_highest_class_in_fold_xgb = list()
    
    for subject, scores in best_scores_dict.items():
        
        '''Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_pt:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_pt[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            pts_baseline_accuracy_highest_class_in_fold_xgb.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        

        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'approx_4':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta'
            clf_str = 'xgb'
            
        elif level == 'approx_5':
            
            ax1.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            
            level_str = 'delta'
            clf_str = 'xgb'
                
                
        elif level == 'detail_5':
            
            ax1.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta_strict'
            clf_str = 'xgb'
            
        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='purple', zorder=5, label=f'Best Score XGBoost for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='purple', zorder=5, label=f'Best Score XGBoost for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return pts_baseline_accuracy_highest_class_in_fold_xgb

# Esempio di utilizzo
save_path_level_4 = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5 = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5_detail = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
pts_baseline_accuracy_highest_class_in_fold_level_4_xgb = plot_best_scores_for_subjects(best_scores_level_4_single_pt_xgb, 'approx_4', save_path_level_4)
pts_baseline_accuracy_highest_class_in_fold_level_5_xgb = plot_best_scores_for_subjects(best_scores_level_5_single_pt_xgb, 'approx_5', save_path_level_5)
pts_baseline_accuracy_highest_class_in_fold_level_5_detail_xgb = plot_best_scores_for_subjects(best_scores_level_5_detail_pt_xgb, 'detail_5', save_path_level_5)

In [ ]:
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('pts_baseline_accuracy_highest_class_in_fold_xgb.pkl', 'wb') as f:
#    pickle.dump(pts_baseline_accuracy_highest_class_in_fold_xgb, f)
    
    
# Salvare l'intero dizionario annidato con pickle
import pickle

with open('best_scores_level_4_single_pt_xgb.pkl', 'wb') as f:
    pickle.dump(best_scores_level_4_single_pt_xgb, f)

with open('best_scores_level_5_single_pt_xgb.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_single_pt_xgb, f)

with open('best_scores_level_5_detail_pt_xgb.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_detail_pt_xgb, f)
    
#print(f"len(pts_baseline_accuracy_highest_class_in_fold_level_4_xgb): {len(pts_baseline_accuracy_highest_class_in_fold_level_4_xgb)}")    
#print(f"len(pts_baseline_accuracy_highest_class_in_fold_level_5_xgb): {len(pts_baseline_accuracy_highest_class_in_fold_level_5_xgb)}")

#import pickle 
# Caricare il dizionario salvato con pickle
#with open('/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations_th.pkl', 'rb') as f:
#   subject_level_concatenations_th = pickle.load(f)

##### **ALL SINGLE Patients (PT01-PT20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)

In [ ]:
new_subject_level_concatenations_pt_1_20.keys()

In [ ]:
#new_subject_level_concatenations_pt_1_20.keys()
#dict_keys(['pt_1', 'pt_2', 'pt_3', 'pt_4', 'pt_5', 'pt_6', 'pt_7', 'pt_8', 'pt_9', 'pt_10', 'pt_11', 'pt_12', 'pt_13', 'pt_14', 'pt_15', 'pt_16'])

#new_subject_level_concatenations_pt_1_20['pt_16'].keys()
#dict_keys(['data', 'labels'])

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO PAZIENTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI FILTERED 1-20Hz

best_scores_filtered_1_20_single_pt_xgb
'''


import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
    # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots_1_20')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    pts_baseline_accuracy_highest_class_in_fold_xgb = list()
    
    for subject, scores in best_scores_dict.items():
        
        ''' Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}_filtered_1_20')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_pt_1_20:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_pt_1_20[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            pts_baseline_accuracy_highest_class_in_fold_xgb.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        
        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'filtered_1_20':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)',  fontsize = 16)
            
            level_str = 'filtered_1_20'
            clf_str = 'xgb'
            

        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='purple', zorder=5, label=f'Best Score XGBoost for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='purple', zorder=5, label=f'Best Score XGBoost for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return pts_baseline_accuracy_highest_class_in_fold_xgb

# Esempio di utilizzo
save_path_filtered_1_20 = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
pts_baseline_accuracy_highest_class_in_fold_1_20_xgb = plot_best_scores_for_subjects(best_scores_filtered_1_20_single_pt_xgb, 'filtered_1_20', save_path_filtered_1_20)


#### **All Patients (PT01-PT20)**

#### Plots of **Grand Average Mean** of Best Single Subject's Accuracy Score Performances 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **NEW VERSION**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_pt = {}
    best_scores_level_5_single_pt = {}
    best_scores_level_5_detail_pt = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_pt_level_4_std" o "all_pt_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_pt_level_4_std" o "all_pt_level_5_std"
            if "all_pt_level_4_std" in file_name or "all_pt_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            #if level == 4 and subject not in best_scores_level_4_single_pt:
            
            if level == 'approx_4' and subject not in best_scores_level_4_single_pt:    
                best_scores_level_4_single_pt[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_pt:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_pt:
                best_scores_level_5_single_pt[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_pt:
                best_scores_level_5_detail_pt[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_pt[subject][window] = max(best_scores_level_4_single_pt[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_pt[subject][window] = max(best_scores_level_5_single_pt[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_pt[subject][window] = max(best_scores_level_5_detail_pt[subject][window], best_score)

    return best_scores_level_4_single_pt, best_scores_level_5_single_pt, best_scores_level_5_detail_pt  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_pt_xgb, best_scores_level_5_single_pt_xgb, best_scores_level_5_detail_pt_xgb = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_pt_xgb keys\033[0m: {best_scores_level_4_single_pt_xgb.keys()}")

for th_key, window_key in best_scores_level_4_single_pt_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_pt_xgb keys\033[0m: {best_scores_level_5_single_pt_xgb.keys()}")

for th_key, window_key in best_scores_level_5_single_pt_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_pt_xgb keys\033[0m: {best_scores_level_5_detail_pt_xgb.keys()}")

for th_key, window_key in best_scores_level_5_detail_pt_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        '''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")
        
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_4 = calculate_mean_and_confidence_interval(best_scores_level_4_single_pt_xgb, n_windows)
statistics_level_5 = calculate_mean_and_confidence_interval(best_scores_level_5_single_pt_xgb, n_windows)
statistics_level_5_detail = calculate_mean_and_confidence_interval(best_scores_level_5_detail_pt_xgb, n_windows)

In [ ]:
'''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
#print(best_scores_level_4_single_pt_xgb['th_1']['0-50'])
#print(best_scores_level_4_single_pt_xgb'th_2']['0-50'])
#print(best_scores_level_4_single_pt_xgb['th_3']['0-50'])
#print()
#print(best_scores_level_4_single_pt_xgb['th_1']['25-75'])
#print(best_scores_level_4_single_pt_xgb['th_2']['25-75'])
#print(best_scores_level_4_single_pt_xgb['th_3']['25-75'])


In [ ]:
type(statistics_level_4)

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
!pwd

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('new_all_pt_concat_reconstructions.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_pt['pt_1'].keys()

In [ ]:
new_all_pt_concat_reconstructions.keys()

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME '''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    subjects_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    os.makedirs(subjects_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 4:
        level_str = 'theta'
    elif level == 5:
        level_str = 'delta'
    elif level == '5_detail':
        level_str = 'theta_strict'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'all_ths_level_{level_str}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    print(f"\n\t\t\t\t\t\033[1mPatients'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_pt_concat_reconstructions.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    
    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)

    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Aggiunge il livello di baseline in base al livello specificato
    #if level == 4:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range')
    #elif level == 5:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range')
    #elif level == '5_detail':
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Detail Range')
    
    '''VECCHIO'''
    
    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
    if level_str == 'theta':
        ax1.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range', fontsize = 16)
        ax2.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range',  fontsize = 16)
        
    elif level_str == 'delta':
        ax1.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)
        ax2.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)

    elif level_str == 'theta_strict':
        ax1.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
        ax2.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
    
    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='purple', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='purple', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='purple', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='purple', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_pts_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(subjects_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_4, 4, save_path)
plot_mean_best_scores_for_window(statistics_level_5, 5, save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail, '5_detail', save_path)

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE E PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    

 # Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_all_pt_concat_reconstructions_1_20.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions_1_20 = pickle.load(f)

In [ ]:
print(new_subject_level_concatenations_pt_1_20.keys())
print()
print(new_subject_level_concatenations_pt_1_20['pt_1'].keys())
print(new_subject_level_concatenations_pt_1_20['pt_1']['data'].shape)
print()
print(new_all_pt_concat_reconstructions_1_20.keys())
print(new_all_pt_concat_reconstructions_1_20['data'].shape)

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''

import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_pt = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_pt:    
                best_scores_filtered_1_20_single_pt[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_pt[subject][window] = max(best_scores_filtered_1_20_single_pt[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_pt

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_pt_xgb = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_pt_xgb keys\033[0m: {best_scores_filtered_1_20_single_pt_xgb.keys()}")

for th_key, window_key in best_scores_filtered_1_20_single_pt_xgb.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        '''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")

        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_1_20 = calculate_mean_and_confidence_interval(best_scores_filtered_1_20_single_pt_xgb, n_windows)

In [ ]:
'''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
#print(best_scores_filtered_1_20_single_pt_xgb['th_1']['0-50'])
#print(best_scores_filtered_1_20_single_pt_xgb['th_2']['0-50'])
#print(best_scores_filtered_1_20_single_pt_xgb['th_3']['0-50'])
#print()
#print(best_scores_filtered_1_20_single_pt_xgb['th_1']['25-75'])
#print(best_scores_filtered_1_20_single_pt_xgb['th_2']['25-75'])
#print(best_scores_filtered_1_20_single_pt_xgb['th_3']['25-75'])

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    data_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    os.makedirs(data_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 'filtered_1_20':
        level_str = 'filtered_1_20'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    #print(f"\n\t\t\t\t\t\033[1mPatients'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_pt_concat_reconstructions_1_20.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}\n\n\n")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    
    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)
    
    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Linea orizzontale per il chance level
    #plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    #plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)')

    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è filtered_1_20, gestisci i titoli per i grafici su ax1 e ax2
    if level == 'filtered_1_20':

        ax1.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 14)
        ax2.set_title(f'XGBoost - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 14)

    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='purple', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='purple', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='purple', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='purple', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_pts_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(data_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'\nPlot salvato in: \n\033[1m{save_file_path}\033[0m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_1_20, 'filtered_1_20', save_path)

## **SVM**

#### **ALL SINGLE Therapists (TH01-TH20)**

#### Automatization of all steps from: 

1) "**subject_level_concatenations_th**" : ricostruzioni 4 e 5° livello wavelet da approx coefficients
2) "**new_subject_level_concatenations_th**":  ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_th_1_20**": EEG preprocessed signal filtered 1-20Hz 


In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)

##### **ALL SINGLE Therapists (TH01-TH15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DELLE RICOSTRUZIONI**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**

In [ ]:
''' SVM GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare


'''


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER SVM'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra il set di combinazioni tra gli iper-parametri, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...

'''

https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html


C-Support Vector Classification.
The implementation is based on libsvm. 
The fit time scales at least quadratically with the number of samples and may be impractical beyond tens of thousands of samples.

For large datasets consider using LinearSVC or SGDClassifier instead, possibly after a Nystroem transformer or other Kernel Approximation.

The multiclass support is handled according to a one-vs-one scheme.

For details on the precise mathematical formulation of 

-the provided kernel functions and 
-how gamma, coef0 and degree affect each other, 

see the corresponding section in the narrative documentation: Kernel functions.

To learn how to tune SVC’s hyperparameters, see the following example: Nested versus non-nested cross-validation

Read more in the User Guide.





# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)


Ad ora, la mia "valid_params_dict_svc" è fatta così:


valid_params_dict_svc = {
    'linear': [{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               {'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               ...], 
    'poly': [{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             {'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             ...], 
    'rbf': [...],
    'sigmoid': [...]
}



Ora, quindi, per accorpare tutti i dizionari contenuti nel tuo dizionario valid_params_dict_svc in un'unica lista di dizionari 
che può essere fornita a RandomizedSearchCV
devo iterare sulle chiavi principali del dizionario e 
concatenare le liste di iper-parametri per ciascun kernel in un'unica lista.

infatti --> https://scikit-learn.org/1.5/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

'params_distributions' dentro RandomizedSearchCV viene accettato come

- param_distributions: dict or list of dicts



# Crea una lista vuota per contenere tutti i parametri
all_params = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params.extend(params_list)



###CHECK PER PRINT VARI

# Ora all_params contiene tutti i dizionari concatenati
#print(f"all_params is:, {type(all_params)}")


# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in enumerate(all_params):
    print(params_list)
    
    
OUTPUT:

----

{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 10, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 100, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}

----

    
'''



# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)

# Crea una lista vuota per contenere tutti i parametri
all_params_svc = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params_svc.extend(params_list)
    
    
print(f"\t\t\t\033[1mAll Valid Testable Params will be among these below\033[0m:\n") 
for param_dict in all_params_svc: 
    
    #print(f"\033[1m{param_dict.keys()}\033[0m, {param_dict.values()}")
    
    print("{", end="")  # Inizia il dizionario
    for i, (key, value) in enumerate(param_dict.items()):
        # Formattazione della chiave in grassetto
        bold_key = f"\033[1m{key}\033[0m"
        
        # Se non è l'ultima coppia, aggiungi una virgola
        if i < len(param_dict) - 1:
            print(f"'{bold_key}': {value}, ", end="")
        else:
            print(f"'{bold_key}': {value}", end="")
    
    print("}")  # Chiude il dizionario e va a capo
    
# Itera attraverso i soggetti


'''OLD VERSION'''
#for subject, levels in subject_level_concatenations_th.items():


'''NEW VERSION'''
for subject, levels in new_subject_level_concatenations_th.items():
    
    
    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO''' 
    #if subject == 'th_16':
    #if subject == 'th_17' or subject == 'th_18' or subject == 'th_19': 
    if subject == 'th_20': 
    
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")
        
        '''NEW VERSION'''
        #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
        params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params'

        # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
        #                                      'delta' = δ,i.e., approx_5 ,
        #                                      'theta_strict' = Θ, i.e., detail_5,
        #                                      'labels') 

        for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'


            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")

            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_std.txt'

            #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\t\033[1m{params_dir}\033[0m"),
            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

            y = levels['labels'] # Estraiamo le labels livello corrente del soggetto corrente

            print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}

            #INIZIALIZZAZIONE SVC

            base_svc = SVC()

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            #invalid_combination_count = 0

            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")



            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_svc,
                        param_distributions = all_params_svc,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:


                        #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                        #calcolato sulla base di una cross-validation a 5 fold. 
                        #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                        #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                        #In sintesi, è il valore medio di accuracy ottenuto 
                        #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                        #per una specifica combinazione di iper-parametri!


                        for i, params in enumerate(rand_search.cv_results_['params']):
                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                #invalid_combination_count += 1
                                print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri
                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH
                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")
        

##### **ALL SINGLE Therapist (TH01-TH15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

- **EEG preprocessed signal**: filtered 1-20


In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun soggetto nel dizionario
for soggetto, dati in new_subject_level_concatenations_th_1_20.items():
    
    # Verifica che 'data' sia presente tra le chiavi
    if 'data' in dati:
        
        # Sotto-seleziona i canali di interesse
        dati_originali = dati['data']  # Estrai i dati
        
        dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali

        # Aggiorna la chiave 'data' con i dati filtrati
        new_subject_level_concatenations_th_1_20[soggetto]['data'] = dati_sottoselezionati

        # Opzionale: stampa di controllo per verificare la nuova forma dei dati
        print(f"Soggetto {soggetto}: {dati_sottoselezionati.shape}")

In [ ]:
##### **ALL SINGLE Therapists (T01-TH15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DAL SEGNALE 1-20Hz**


''' SVM GIUSTO! TERAPISTI NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare


'''


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER SVM'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra il set di combinazioni tra gli iper-parametri, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...

'''

https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html


C-Support Vector Classification.
The implementation is based on libsvm. 
The fit time scales at least quadratically with the number of samples and may be impractical beyond tens of thousands of samples.

For large datasets consider using LinearSVC or SGDClassifier instead, possibly after a Nystroem transformer or other Kernel Approximation.

The multiclass support is handled according to a one-vs-one scheme.

For details on the precise mathematical formulation of 

-the provided kernel functions and 
-how gamma, coef0 and degree affect each other, 

see the corresponding section in the narrative documentation: Kernel functions.

To learn how to tune SVC’s hyperparameters, see the following example: Nested versus non-nested cross-validation

Read more in the User Guide.





# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)


Ad ora, la mia "valid_params_dict_svc" è fatta così:


valid_params_dict_svc = {
    'linear': [{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               {'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               ...], 
    'poly': [{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             {'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             ...], 
    'rbf': [...],
    'sigmoid': [...]
}



Ora, quindi, per accorpare tutti i dizionari contenuti nel tuo dizionario valid_params_dict_svc in un'unica lista di dizionari 
che può essere fornita a RandomizedSearchCV
devo iterare sulle chiavi principali del dizionario e 
concatenare le liste di iper-parametri per ciascun kernel in un'unica lista.

infatti --> https://scikit-learn.org/1.5/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

'params_distributions' dentro RandomizedSearchCV viene accettato come

- param_distributions: dict or list of dicts



# Crea una lista vuota per contenere tutti i parametri
all_params = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params.extend(params_list)



###CHECK PER PRINT VARI

# Ora all_params contiene tutti i dizionari concatenati
#print(f"all_params is:, {type(all_params)}")


# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in enumerate(all_params):
    print(params_list)
    
    
OUTPUT:

----

{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 10, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 100, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}

----

    
'''



# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)

# Crea una lista vuota per contenere tutti i parametri
all_params_svc = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params_svc.extend(params_list)
    
    
print(f"\t\t\t\033[1mAll Valid Testable Params will be among these below\033[0m:\n") 
for param_dict in all_params_svc: 
    
    #print(f"\033[1m{param_dict.keys()}\033[0m, {param_dict.values()}")
    
    print("{", end="")  # Inizia il dizionario
    for i, (key, value) in enumerate(param_dict.items()):
        # Formattazione della chiave in grassetto
        bold_key = f"\033[1m{key}\033[0m"
        
        # Se non è l'ultima coppia, aggiungi una virgola
        if i < len(param_dict) - 1:
            print(f"'{bold_key}': {value}, ", end="")
        else:
            print(f"'{bold_key}': {value}", end="")
    
    print("}")  # Chiude il dizionario e va a capo
    

# Itera attraverso i soggetti
#for subject, levels in subject_level_concatenations_th_1_20.items():

for subject, subj_dict in new_subject_level_concatenations_th_1_20.items():
    
    #if subject == 'th_16':
    #if subject == 'th_17' or subject == 'th_18' or subject == 'th_19':
    
    #if subject == 'th_20':
        
    print(f"\t\t\t\t\t\t\n\nCurrent Subject \033[1m{subject}\033[0m")

    print(f"\n\n\033[1mExtraction of Data\033[0m from Subject \033[1m{subject}\033[0m from Original Filtered Signal in \033[1m1-20Hz\033[0m")

    X = subj_dict['data'] # Estraiamo i dati del soggetto corrente

    y = subj_dict['labels'] # Estraiamo le labels livello corrente del soggetto corrente

    #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
    params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20'

    #FILE PATH DINAMICA PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
    #A SECONDA DEL SOGGETTO E LIVELLO DI RICOSTRUZIONE DEI DATI PRESI IN ESAME 

    # Costruzione del percorso del file in maniera dinamica
    params_file_path = f'{params_dir}/optimized_params_{subject}_filtered_1_20_std.txt'

    if not os.path.exists(params_dir):
        os.makedirs(params_dir)

    #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\033[1m{params_dir}\033[0m"),
    #print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

    #Path per combinazioni iperparametri NON valide
    #invalid_params_file_path = f'{params_dir}/invalid_params_{subject}_filtered_1_20_std.txt'

    print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

    y = y.astype(int) 

    print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


    # Calcola il numero totale di etichette livello 4/5°
    label_counts = np.unique(y, return_counts = True)[1]
    total_labels = len(y)

    # Calcola la percentuale di ciascuna classe
    class_proportions = label_counts / total_labels * 100

    print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

    # Calcola i pesi delle classi come l'inverso delle proporzioni
    class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

    # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
    class_weights /= class_weights.sum()

    print(f"\n\033[1mClass Weights {class_weights}\033[0m")

    # Crea un dizionario per class_weight
    class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}

    '''INIZIALIZZAZIONE XGBOOST'''

    base_svc = SVC()

    # Memorizza il tempo di inizio
    start_time = time.time()

    # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
    execution_times = []

    # Contatori per combinazioni valide e non valide
    valid_combination_count = 0
    invalid_combination_count = 0

    # File di output per i parametri ottimizzati
    with open(params_file_path, 'w') as f:
        f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

    # File di output per i parametri ottimizzati NON validi
    #with open(invalid_params_file_path, 'w') as invalid_f:
    #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


    '''INIZIALIZZAZIONE RANDOM SEARCH'''

    # Lista per memorizzare i risultati delle finestre
    window_results = []

    # Creazione della finestra scorrevole con step e dimensioni desiderate
    n_samples = X.shape[2]
    window_size = 50
    step_size = 25
    n_windows = (n_samples - window_size) // step_size + 1


    #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

    # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

    for window_start in range(0, n_samples - window_size + 1, step_size):

        # Memorizza il tempo di inizio per il punto temporale corrente
        time_point_start = time.time()

        # Definiamo la finestra corrente
        window_end = window_start + window_size

        print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

        X_window = X[:, :, window_start:window_end]
        #print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

        # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
        X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
        #print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

        # Standardizza i dati della finestra corrente
        scaler = StandardScaler()
        X_window_standardized = scaler.fit_transform(X_window_reshaped)
        #print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

        try:
            print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


            rand_search = RandomizedSearchCV(
                estimator = base_svc,
                param_distributions = all_params_svc,
                scoring ='accuracy',
                n_iter = 100,
                verbose = 1,
                n_jobs = -1
            )


            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

            # Esegui RandomizedSearchCV sulla finestra corrente
            rand_search.fit(X_window_standardized, y)


            # Controlla il numero totale di combinazioni testate
            total_combinations_tested = len(rand_search.cv_results_['params'])
            #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

            # Salva tutte le combinazioni testate per la finestra corrente
            with open(params_file_path, 'a') as f:

                '''
                Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                calcolato sulla base di una cross-validation a 5 fold. 
                Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                In sintesi, è il valore medio di accuracy ottenuto 
                mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                per una specifica combinazione di iper-parametri!
                '''

                for i, params in enumerate(rand_search.cv_results_['params']):
                    score = rand_search.cv_results_['mean_test_score'][i]
                    f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                for params in rand_search.cv_results_['params']:
                    if params:
                        valid_combination_count += 1
                    else:
                        invalid_combination_count += 1
                        print(f"Invalid combination found: {params}")

                #QUI

                # Ottieni il modello con i migliori iper-parametri
                best_model_params = rand_search.best_params_


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH
                best_score = rand_search.best_score_


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                # Memorizza i risultati della finestra corrente
                window_results.append({
                    'window_start': window_start,
                    'window_end': window_end,
                    'best_params': best_model_params,
                    'best_score': best_score
                })


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

            #Salva i parametri migliori per la finestra corrente in una riga del file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                f.write('\n')

        except Exception as e:

            print(f'Error: {e}')

            # Scrivi la combinazione non valida nel file di output
            #with open(invalid_params_file_path, 'a') as invalid_f:
            #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
            #continue


            # Memorizza il tempo di fine per il punto temporale corrente
            time_point_end = time.time()

            # Calcola il tempo di esecuzione per il punto temporale corrente
            time_point_elapsed = time_point_end - time_point_start

            # Aggiungi il tempo di esecuzione alla lista
            execution_times.append(time_point_elapsed)

            # Stampa i risultati per il punto temporale corrente
            #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
            #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
            #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
            #print()
            #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
            #print()

    # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

    # Definisci il range generale delle finestre che vuoi analizzare
    general_range = [0, 300]  # Puoi modificare il range se necessario

    # Filtra i risultati delle finestre nel range desiderato
    general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

    # Controlla se ci sono risultati validi all'interno del range specificato
    if general_results:

        # Trova la finestra con il punteggio migliore
        best_general_window = max(general_results, key=lambda x: x['best_score'])

        # Trova i parametri migliori per questa finestra specifica (se disponibili)
        best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
        best_general_window['best_params'] = best_params

        # Stampa le informazioni sulla finestra migliore trovata
        #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
        #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
        #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

    else:
        print("No valid windows found in the specified range.")


    # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
    window_results.append({
        'Best window_start': best_general_window['window_start'] if general_results else None,
        'Best window_end': best_general_window['window_end'] if general_results else None,
        'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
        'best_score': best_general_window['best_score'] if general_results else None
    })

    # Calcola il tempo di esecuzione totale
    end_time = time.time()
    total_execution_time = end_time - start_time

    #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
    #print()
    #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
    #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

    # Aggiungi il risultato della migliore finestra generale al file di testo
    with open(params_file_path, 'a') as f:
        f.write('\n')
        if general_results:
            best_general_window = max(general_results, key=lambda x: x['best_score'])
            f.write(f"BEST WINDOW OVERALL: "),
            f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
            f.write(f"\nBest Window End: {best_general_window['window_end']}"),
            f.write(f"\nBest Score: {best_general_window['best_score']}")

            if best_general_window['best_params'] is not None:
                    f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
            else:
                f.write("No valid windows found in the specified range.\n")

            f.write('\n')
            f.write(f"Total execution time: {total_execution_time} seconds\n")
            f.write(f"Number of valid combinations: {valid_combination_count}\n")
            f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")


#### **ALL SINGLE Therapists (TH01-TH20) for **COUPLED EXPERIMENTAL CONDITIONS****

#### Automatization of all steps from: 

1) "**new_subject_level_concatenations_coupled_exp_th**" ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_coupled_exp_th_1_20**": EEG preprocessed signal filtered 1-20Hz 

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''


#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
#    new_subject_level_concatenations_th = pickle.load(f)
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle
import numpy as np


base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'


with open(f'{base_dir}/new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open(f'{base_dir}/new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open(f'{base_dir}/new_subject_level_concatenations_coupled_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open(f'{base_dir}/new_subject_level_concatenations_coupled_exp_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th_1_20 = pickle.load(f)
    


    
    
#PER SALVARE I FILE
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('NOME DEL FILE.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations, f)


#subject_level_concatenations_th['th_1'].keys()

In [ ]:
th_fam.keys

In [ ]:
print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_th\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()}")
print()
print(f"\033[1mData Shape\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['data'].shape}")

In [ ]:
np.unique(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['labels'],return_counts=True)

##### **Descrizione degli step nel codice per ottenere e salvare nelle paths le best score performances per il level 4 e 5 dalle ricostruzioni**:

Vorrei in questo caso, per velocizzare, iterare su 

subject_level_concatenations, che ha questa struttura...

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


al cui interno ha per ogni chiave di primo ordine, un altro dizionario annidato, che è fatto di queste chiavi


dict_keys(['theta', 'delta', 'labels'])

dentro 'theta' e 'delta' ci sono tutti i dati di tutte le condizioni sperimentali del singolo soggetto

del tipo 'theta' o 'delta' conterrà un array con shape

(204, 3, 300)

con 1° dimensione i trial, poi i canali, poi i punti di ogni trial (campioni EEG)

e dentro 'labels' ho invece l'array delle labels concatenate...
(204,)


<br>


Ora però, vorrei che ... 

Se ad esempio nel soggetto 'th_1' entri nella chiave 'theta', 

allora poi il file corrispondente .txt deve essere scritto con una path dinamica, che cambia a seconda 
- sia del soggetto iterato
- sia del livello di ricostruzione dei dati

Ossia:

la "params_dir" è fissa

mentre 

"params_file_path" è dinamica, e cambia a seconda del soggetto iterato e del livello. 

Per cui sarà una composizione di stringhe fisse e stringhe 'mobili', ossia

'params_file_path' = 'optimized_params_' + {subject} dove subject dovrebbe essere una lista di stringhe che si preleva dalle chiavi di primo ordine di "subject_level_concatenations" che erano

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


seguito da "_level_{level}_std" dove {level} dipende dal nome della chiave del sotto-dizionario iterato per ogni soggetto...

Ossia, ad esempio dentro il sotto-dizionario del primo soggetto di "subject_level_concatenations" cioè

subject_level_concatenations['th_1'], 

Se la sua sotto-chiave è 'theta' allora il level = 4, se la chiave è 'delta' allora il level = 5, 



Quindi la costruzione finale della path dinamica del file specifico per il soggetto 1 deve essere

 
params_file_path = 'optimized_params_' +'{subject}' + "_level_{level}_std.txt"

e sarà se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_1' + "_level_4_std.txt"


e sarà se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_1' + "_level_5_std.txt"


in questo modo, farei un loop unico su tutte le sottochiavi dei dizionari annidati dentro 
"subject_level_concatenations" 

ossia 
dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

e per ognuno vedo se la sua sotto-chiave sarà 'theta' o 'delta' e creerà dei file .txt corrispondenti nella param_dir che gli ho chiesto...

Il resto del codice non toccarlo invece, perché dovrebbe creare dei file .txt per ogni soggetto per ogni livello di ricostruzione dei dati,
e salverà le analisi nel file .txt corrispondente



Ad esempio, continuando col soggetto 2:

la costruzione finale della path dinamica del file specifico per il soggetto 2

Sarà, se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_2' + "_level_4_std.txt"


e sarà, se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_2' + "_level_5_std.txt"


e così via per tutti gli altri soggetti




##### **ALL SINGLE Therapists (TH01-TH16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DALLE RICOSTRUZIONI** 

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**


###### **ISTRUZIONI PER MODIFICHE AL CASO 2 CLASSI**

Allora, andiamo per step:

**1)** la nuova variabile sulla quale iterare è new_subject_level_concatenations_coupled_exp_th

che è fatta con questa struttura

print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_th\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()}")

OUTPUT:

Dataset Organization: new_subject_level_concatenations_coupled_exp_th

First Order Key: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16'])

Second Order Key: dict_keys(['theta', 'delta', 'theta_strict'])

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

Fourth Order Key: dict_keys(['data', 'labels'])

quindi significa che, per ogni soggetto, tu dovrai entrare nella sotto sotto chiave relativa ai livelli di ricostruzione del segnale 

dict_keys(['theta', 'delta', 'theta_strict'])

per ognuna di queste, avrai appunto delle altre sotto-sotto-sotto chiavi, che sono le condizioni sperimentali, sulle quali dovrai entrare che sono 

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

dopodiché dentro ognuna di queste, dovrai entrare ulteriormente dentro ciascuna sotto chiave di quarto livello:

la prima, che fa riferimento ai dati('data') il cui valore (array numpy() verrà assegnato ad X nel codice, e 
la seconda, la chiave delle labels ('labels') il cui valore verrà assegnato ad Y...

**2)** questa parte relativa ai print

 for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'

voglio che poi abbia degli altri if, nel senso che vorrei che iterando su ogni livello, voglio che venga applicata la stessa logica dei printing di qui sopra, ma alle chiavi del 3° livello, ossia quelle che fanno riferimento alle condizioni sperimentali...

ossia, 

voglio che ci sia scritto per le X

print(f"\n\033[1mExtraction of Data\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

e voglio che ci sia scritto per le Y

print(f"\n\033[1mExtraction of Labels\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

dove 

"experimental_condition" farà riferimento alla chiave della condizione sperimentale iterata in quel loop, e 

"level_key" invece farà riferimento alle chiavi del 2° livello, ossia a quelle che si riferiscono allo specifico livello di ricostruzione del segnale per il quale io sto estraendo i dati e le labels al ciclo corrente...

In questo modo, dovrei avere un'idea dai print del mio codice, quando viene eseguito, su quale soggetto, quale livello e quale condizione sperimentale sta eseguendo i calcoli.. 

**3)** voglio che vengano create dei folder nuovi per appendere i risultati di tutte le elaborazioni da parte dei vari modelli e che saranno queste due cartelle

"EEG_50_window_25_overlap_coupled_exp_cond" 
"single_therapist_optimized_params_coupled_exp_cond"
 
ossia la mia directory dovrebbe diventare

params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond'

per cui, se "EEG_50_window_25_overlap_coupled_exp_cond" né "single_therapist_optimized_params_coupled_exp_cond" non sono state create, allora andranno create...

**4)** la creazione del nome del file relativo ad un determinato soggetto dovrà essere formato in questo modo

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

dove, ricorda, "experimental_condition" farà riferimento alle insieme delle stringhe che compongono la chiave della condizione sperimentale iterata in quel loop (chiavi di 3° livello di "new_subject_level_concatenations_coupled_exp_th" 

del tipo potrebbe essere

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

Con ad esempio:

subject = th_1
level = theta 
experimental_condition = baseline_vs_th_resp

per cui sarebbe 

f'{params_dir}/optimized_params_th_1_level_theta_baseline_vs_th_resp_std.txt'

**5)** al momento, il settaggio degli iper-parametri è impostato per anche per i casi multi-nomiali ma in questo caso il codice verrà usato per task di classificazione binaria...

per cui, voglio essere sicuro che l'impostazione attuale vada anche bene per i casi semplicemente binomiali, ossia di due possibili classi solo...

per farlo, ti do il link della pagina della Logistic Regression, in modo che tu mi dica se l'attuale implementazione sia corretta....

https://scikit-learn.org/1.5/modules/generated/sklearn.linear_model.LogisticRegression.html


**6)** Fai le modifiche a quello che ti ho chiesto, non azzardare cose in più od in meno, vorrei che ti attenessi a ciò che ti ho chiesto...


##### **IMPLEMENTATION SVM FOR COUPLED EXPERIMENTAL CONDITIONS**

In [ ]:
new_subject_level_concatenations_coupled_exp_th['th_2']['theta']['baseline_vs_th_resp'].keys()


#TROVARE INDICI DELLE LABELS ASSOCIATE
labels_array = new_subject_level_concatenations_coupled_exp_th['th_5']['delta']['th_resp_vs_pt_resp']['labels']
indices_0 = np.where(np.isin(labels_array, [0]))[0]
indices_1 = np.where(np.isin(labels_array, [1]))[0]
print(indices_0)
print()
print(indices_1)

In [ ]:
''' SVM GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare


'''


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER SVM'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra il set di combinazioni tra gli iper-parametri, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...

'''

https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html


C-Support Vector Classification.
The implementation is based on libsvm. 
The fit time scales at least quadratically with the number of samples and may be impractical beyond tens of thousands of samples.

For large datasets consider using LinearSVC or SGDClassifier instead, possibly after a Nystroem transformer or other Kernel Approximation.

The multiclass support is handled according to a one-vs-one scheme.

For details on the precise mathematical formulation of 

-the provided kernel functions and 
-how gamma, coef0 and degree affect each other, 

see the corresponding section in the narrative documentation: Kernel functions.

To learn how to tune SVC’s hyperparameters, see the following example: Nested versus non-nested cross-validation

Read more in the User Guide.





# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)


Ad ora, la mia "valid_params_dict_svc" è fatta così:


valid_params_dict_svc = {
    'linear': [{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               {'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               ...], 
    'poly': [{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             {'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             ...], 
    'rbf': [...],
    'sigmoid': [...]
}



Ora, quindi, per accorpare tutti i dizionari contenuti nel tuo dizionario valid_params_dict_svc in un'unica lista di dizionari 
che può essere fornita a RandomizedSearchCV
devo iterare sulle chiavi principali del dizionario e 
concatenare le liste di iper-parametri per ciascun kernel in un'unica lista.

infatti --> https://scikit-learn.org/1.5/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

'params_distributions' dentro RandomizedSearchCV viene accettato come

- param_distributions: dict or list of dicts



# Crea una lista vuota per contenere tutti i parametri
all_params = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params.extend(params_list)



###CHECK PER PRINT VARI

# Ora all_params contiene tutti i dizionari concatenati
#print(f"all_params is:, {type(all_params)}")


# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in enumerate(all_params):
    print(params_list)
    
    
OUTPUT:

----

{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 10, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 100, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}

----

    
'''



# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)

# Crea una lista vuota per contenere tutti i parametri
all_params_svc = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params_svc.extend(params_list)
    
    
print(f"\t\t\t\033[1mAll Valid Testable Params will be among these below\033[0m:\n") 
for param_dict in all_params_svc: 
    
    #print(f"\033[1m{param_dict.keys()}\033[0m, {param_dict.values()}")
    
    print("{", end="")  # Inizia il dizionario
    for i, (key, value) in enumerate(param_dict.items()):
        # Formattazione della chiave in grassetto
        bold_key = f"\033[1m{key}\033[0m"
        
        # Se non è l'ultima coppia, aggiungi una virgola
        if i < len(param_dict) - 1:
            print(f"'{bold_key}': {value}, ", end="")
        else:
            print(f"'{bold_key}': {value}", end="")
    
    print("}")  # Chiude il dizionario e va a capo
    
# Itera attraverso i soggetti

'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond"

# Iterazione sulla struttura `new_subject_level_concatenations_coupled_exp_th`

for subject, levels in new_subject_level_concatenations_coupled_exp_th.items():
    
    #if subject == 'th_17' or subject == 'th_18' or subject == 'th_19':
    
    #if subject == 'th_20':
        
    print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")

    for level_key, experimental_condition in levels.items():

        # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
        #                                      'delta' = δ,i.e., approx_5 ,
        #                                      'theta_strict' = Θ, i.e., detail_5,
        #                                      'labels') 

        # Identificazione del livello
        if level_key == 'theta':
            level = "approx_4"


        elif level_key == 'delta':
            level = "approx_5"


        elif level_key == 'theta_strict':
            level = "detail_5"

        else:
            continue  # Ignora livelli non rilevanti


        print(f"\nProcessing Data \033[1m from Level: \033[1m{level_key}\033[0m for Subject \033[1m{subject}\033[0m")

        for condition, data_dict in experimental_condition.items():

            # Estrazione dei dati e delle label
            X = data_dict['data'] # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente

            # Messaggi di log per dati e label
            print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

            print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

            y = data_dict['labels'] # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente


            '''NEW VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            params_dir = params_dir

            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f"{params_dir}/optimized_params_{subject}_level_{level}_{condition}_std.txt"

            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")
            print(f"\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE SVC

            base_svc = SVC()

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0

            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")



            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_svc,
                        param_distributions = all_params_svc,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:


                        #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                        #calcolato sulla base di una cross-validation a 5 fold. 
                        #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                        #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                        #In sintesi, è il valore medio di accuracy ottenuto 
                        #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                        #per una specifica combinazione di iper-parametri!


                        for i, params in enumerate(rand_search.cv_results_['params']):
                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                invalid_combination_count += 1
                                #print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri
                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH
                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")

##### **ALL SINGLE Therapists (TH01-TH16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **EEG preprocessed signal**: filtered 1-20

In [ ]:
#new_subject_level_concatenations_pt_1_20.keys()
#new_subject_level_concatenations_pt_1_20['pt_1'].keys()

#new_subject_level_concatenations_coupled_exp_pt.keys()

#new_subject_level_concatenations_coupled_exp_pt_1_20.keys()
#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1'].keys()


#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp'].keys()

In [ ]:
import pickle
import numpy as np


with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th_1_20 = pickle.load(f)

In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun livello temporale (th_1, th_2, ..., th_16)
for id_subj in new_subject_level_concatenations_coupled_exp_th_1_20.keys():
    
    # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
    for exp_cond in new_subject_level_concatenations_coupled_exp_th_1_20[id_subj].keys():
        
        # Verifica che 'data' sia presente tra le chiavi della condizione
        if 'data' in new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]:
            
            # Estrai i dati originali
            dati_originali = new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]['data']
            
            # Sotto-seleziona i canali di interesse
            dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali
            
            # Aggiorna la chiave 'data' con i dati filtrati
            new_subject_level_concatenations_coupled_exp_th_1_20[id_subj][exp_cond]['data'] = dati_sottoselezionati

            # Opzionale: stampa di controllo per verificare la nuova forma dei dati
            print(f"Subj \033[1m{id_subj}\033[0m, Condizione \033[1m{exp_cond}\033[0m: {dati_sottoselezionati.shape}")

In [ ]:
new_subject_level_concatenations_coupled_exp_th_1_20.keys()
np.shape(new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp']['data'])

In [ ]:
''' SVM GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare


'''


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER SVM'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra il set di combinazioni tra gli iper-parametri, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...

'''

https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html


C-Support Vector Classification.
The implementation is based on libsvm. 
The fit time scales at least quadratically with the number of samples and may be impractical beyond tens of thousands of samples.

For large datasets consider using LinearSVC or SGDClassifier instead, possibly after a Nystroem transformer or other Kernel Approximation.

The multiclass support is handled according to a one-vs-one scheme.

For details on the precise mathematical formulation of 

-the provided kernel functions and 
-how gamma, coef0 and degree affect each other, 

see the corresponding section in the narrative documentation: Kernel functions.

To learn how to tune SVC’s hyperparameters, see the following example: Nested versus non-nested cross-validation

Read more in the User Guide.





# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)


Ad ora, la mia "valid_params_dict_svc" è fatta così:


valid_params_dict_svc = {
    'linear': [{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               {'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               ...], 
    'poly': [{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             {'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             ...], 
    'rbf': [...],
    'sigmoid': [...]
}



Ora, quindi, per accorpare tutti i dizionari contenuti nel tuo dizionario valid_params_dict_svc in un'unica lista di dizionari 
che può essere fornita a RandomizedSearchCV
devo iterare sulle chiavi principali del dizionario e 
concatenare le liste di iper-parametri per ciascun kernel in un'unica lista.

infatti --> https://scikit-learn.org/1.5/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

'params_distributions' dentro RandomizedSearchCV viene accettato come

- param_distributions: dict or list of dicts



# Crea una lista vuota per contenere tutti i parametri
all_params = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params.extend(params_list)



###CHECK PER PRINT VARI

# Ora all_params contiene tutti i dizionari concatenati
#print(f"all_params is:, {type(all_params)}")


# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in enumerate(all_params):
    print(params_list)
    
    
OUTPUT:

----

{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 10, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 100, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}

----

    
'''



# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)

# Crea una lista vuota per contenere tutti i parametri
all_params_svc = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params_svc.extend(params_list)
    
    
print(f"\t\t\t\033[1mAll Valid Testable Params will be among these below\033[0m:\n") 
for param_dict in all_params_svc: 
    
    #print(f"\033[1m{param_dict.keys()}\033[0m, {param_dict.values()}")
    
    print("{", end="")  # Inizia il dizionario
    for i, (key, value) in enumerate(param_dict.items()):
        # Formattazione della chiave in grassetto
        bold_key = f"\033[1m{key}\033[0m"
        
        # Se non è l'ultima coppia, aggiungi una virgola
        if i < len(param_dict) - 1:
            print(f"'{bold_key}': {value}, ", end="")
        else:
            print(f"'{bold_key}': {value}", end="")
    
    print("}")  # Chiude il dizionario e va a capo
    

#ATTENZIONE CAMBIA PATH CLASSIFIER!

'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond_1_20"


for idx_subj, subject_data in new_subject_level_concatenations_coupled_exp_th_1_20.items():
    
    level_str = 'filtered_1_20'
    
    #if idx_subj == 'th_17' or idx_subj == 'th_18' or idx_subj == 'th_19':
    
    if idx_subj == 'th_20':
    
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {idx_subj}\033[0m\n\n")

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        #for condition in new_subject_level_concatenations_coupled_exp_th_1_20[idx_subj].keys():

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        for condition, condition_data in subject_data.items():

            #print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Creazione stringa per salvataggio files ('filtered_1_20')
            #level_str == 'filtered_1_20'

            print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente
            #X = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['data']

            # Estrazione dei dati e delle etichette
            X = condition_data['data']


            # Messaggi di log per dati e label
            print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente
            #y = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['labels'] 

            y = condition_data['labels']

            print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            '''NEW VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            params_dir = params_dir

            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f"{params_dir}/optimized_params_{idx_subj}_level_{level_str}_{condition}_std.txt"

            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{idx_subj}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")

            print(f"\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE SVC

            base_svc = SVC()

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0

            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_svc,
                        param_distributions = all_params_svc,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:


                        #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                        #calcolato sulla base di una cross-validation a 5 fold. 
                        #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                        #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                        #In sintesi, è il valore medio di accuracy ottenuto 
                        #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                        #per una specifica combinazione di iper-parametri!


                        for i, params in enumerate(rand_search.cv_results_['params']):
                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                invalid_combination_count += 1
                                #print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri
                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH
                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")


#### **ALL SINGLE Therapists (TH01-TH20)**

#### Plots of **EACH SINGLE Subject's Accuracy Score Performances** 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**


##### **ALL SINGLE Therapists (TH01-TH19) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI - OLD VERSION**

##### **ALL SINGLE Therapists (TH01-TH19) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_th = {}
    best_scores_level_5_single_th = {}
    best_scores_level_5_detail_th = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "all_th_level_4_std" in file_name or "all_th_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            #if level == 4 and subject not in best_scores_level_4_single_th:
            if level == 'approx_4' and subject not in best_scores_level_4_single_th:    
                best_scores_level_4_single_th[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_th:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_th:
                best_scores_level_5_single_th[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_th:
                best_scores_level_5_detail_th[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_th[subject][window] = max(best_scores_level_4_single_th[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_th[subject][window] = max(best_scores_level_5_single_th[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_th[subject][window] = max(best_scores_level_5_detail_th[subject][window], best_score)

    return best_scores_level_4_single_th, best_scores_level_5_single_th, best_scores_level_5_detail_th  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_th_svm, best_scores_level_5_single_th_svm, best_scores_level_5_detail_th_svm = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_th_svm keys\033[0m: {best_scores_level_4_single_th_svm.keys()}")

for th_key, window_key in best_scores_level_4_single_th_svm.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_th_svm keys\033[0m: {best_scores_level_5_single_th_svm.keys()}")

for th_key, window_key in best_scores_level_5_single_th_svm.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_th_svm keys\033[0m: {best_scores_level_5_detail_th_svm.keys()}")

for th_key, window_key in best_scores_level_5_detail_th_svm.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

##### **ALL SINGLE Therapists (TH01-TH19) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER EEG 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_th = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_th:    
                best_scores_filtered_1_20_single_th[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_th[subject][window] = max(best_scores_filtered_1_20_single_th[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_th

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_th_svm = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_th_svm keys\033[0m: {best_scores_filtered_1_20_single_th_svm.keys()}")

for th_key, window_key in best_scores_filtered_1_20_single_th_svm.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
#pwd
#cd ..
#cd New_Plots_Sliding_Estimator_MNE

#path corretta --> cd Plots_Sliding_Estimator_MNE
#path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"

#Comandi da eseguire

#!pwd
#cd Plots_Sliding_Estimator_MNE


import pickle

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_filtered_1_20_single_th_svm.pkl', 'wb') as file:
    pickle.dump(best_scores_filtered_1_20_single_th_svm, file)

#print("Dati concantenati dei Singoli Terapisti salvati in 'subject_level_concatenations_th_1_20.pkl'")

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI - OLD VERSION**

##### **ALL SINGLE Therapist (TH01-TH20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX & LEVEL 5 DA COEFF DETAIL DELLE RICOSTRUZIONI**

In [ ]:
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO TERAPISTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI APPROX 4, APPROX 5 e DETAIL 5

best_scores_level_4_single_th_svm, 
best_scores_level_5_single_th_svm,
best_scores_level_5_detail_th_svm
'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
    # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    ths_baseline_accuracy_highest_class_in_fold_svm = list()
    
    for subject, scores in best_scores_dict.items():
        
        '''Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_th:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_th[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            ths_baseline_accuracy_highest_class_in_fold_svm.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        

        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'approx_4':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta'
            clf_str = 'svm'
            
        elif level == 'approx_5':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            
            level_str = 'delta'
            clf_str = 'svm'
                
                
        elif level == 'detail_5':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta_strict'
            clf_str = 'svm'
            
        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='b', zorder=5, label=f'Best Score SVM for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='b', zorder=5, label=f'Best Score SVM for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return ths_baseline_accuracy_highest_class_in_fold_svm

# Esempio di utilizzo
save_path_level_4 = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5 = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5_detail = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
ths_baseline_accuracy_highest_class_in_fold_level_4_svm = plot_best_scores_for_subjects(best_scores_level_4_single_th_svm, 'approx_4', save_path_level_4)
ths_baseline_accuracy_highest_class_in_fold_level_5_smv = plot_best_scores_for_subjects(best_scores_level_5_single_th_svm, 'approx_5', save_path_level_5)
ths_baseline_accuracy_highest_class_in_fold_level_5_detail_svm = plot_best_scores_for_subjects(best_scores_level_5_detail_th_svm, 'detail_5', save_path_level_5)

In [ ]:
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#import pickle

# Salvare l'intero dizionario annidato con pickle
#with open('ths_baseline_accuracy_highest_class_in_fold_svm.pkl', 'wb') as f:
#    pickle.dump(ths_baseline_accuracy_highest_class_in_fold_svm, f)
    

# Salvare l'intero dizionario annidato con pickle
import pickle

with open('best_scores_level_4_single_th_svm.pkl', 'wb') as f:
    pickle.dump(best_scores_level_4_single_th_svm, f)

with open('best_scores_level_5_single_th_svm.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_single_th_svm, f)
    
with open('best_scores_level_5_detail_th_svm.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_detail_th_svm, f)
    
#print(f"len(pts_baseline_accuracy_highest_class_in_fold_level_4_xgb): {len(pts_baseline_accuracy_highest_class_in_fold_level_4_xgb)}")    
#print(f"len(pts_baseline_accuracy_highest_class_in_fold_level_5_xgb): {len(pts_baseline_accuracy_highest_class_in_fold_level_5_xgb)}")


#import pickle 
# Caricare il dizionario salvato con pickle
#with open('/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations_th.pkl', 'rb') as f:
#   subject_level_concatenations_th = pickle.load(f)

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)

In [ ]:
#new_subject_level_concatenations_th_1_20.keys()
#dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16'])

#new_subject_level_concatenations_th_1_20['th_16'].keys()
#dict_keys(['data', 'labels'])

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO TERAPISTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI FILTERED 1-20Hz

best_scores_filtered_1_20_single_th_svm
'''


import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
    # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots_1_20')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    ths_baseline_accuracy_highest_class_in_fold_svm = list()
    
    for subject, scores in best_scores_dict.items():
        
        ''' Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}_filtered_1_20')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_th_1_20:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_th_1_20[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            ths_baseline_accuracy_highest_class_in_fold_svm.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        
        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'filtered_1_20':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)',  fontsize = 16)
            
            level_str = 'filtered_1_20'
            clf_str = 'svm'
            

        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus Period (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='b', zorder=5, label=f'Best Score SVM for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='b', zorder=5, label=f'Best Score SVM for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return ths_baseline_accuracy_highest_class_in_fold_svm

# Esempio di utilizzo
save_path_filtered_1_20 = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
ths_baseline_accuracy_highest_class_in_fold_1_20_svm = plot_best_scores_for_subjects(best_scores_filtered_1_20_single_th_svm, 'filtered_1_20', save_path_filtered_1_20)


#### **All Therapists (TH01-TH20)**

#### Plots of **Grand Average Mean** of Best Single Subject's Accuracy Score Performances 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **NEW VERSION**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_th = {}
    best_scores_level_5_single_th = {}
    best_scores_level_5_detail_th = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "all_th_level_4_std" in file_name or "all_th_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            #if level == 4 and subject not in best_scores_level_4_single_th:
            
            if level == 'approx_4' and subject not in best_scores_level_4_single_th:    
                best_scores_level_4_single_th[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_th:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_th:
                best_scores_level_5_single_th[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_th:
                best_scores_level_5_detail_th[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_th[subject][window] = max(best_scores_level_4_single_th[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_th[subject][window] = max(best_scores_level_5_single_th[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_th[subject][window] = max(best_scores_level_5_detail_th[subject][window], best_score)

    return best_scores_level_4_single_th, best_scores_level_5_single_th, best_scores_level_5_detail_th  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_th_svm, best_scores_level_5_single_th_svm, best_scores_level_5_detail_th_svm = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_th_svm keys\033[0m: {best_scores_level_4_single_th_svm.keys()}")

for th_key, window_key in best_scores_level_4_single_th_svm.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_th_svm keys\033[0m: {best_scores_level_5_single_th_svm.keys()}")

for th_key, window_key in best_scores_level_5_single_th_svm.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_th_svm keys\033[0m: {best_scores_level_5_detail_th_svm.keys()}")

for th_key, window_key in best_scores_level_5_detail_th_svm.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        '''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")

        
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_4 = calculate_mean_and_confidence_interval(best_scores_level_4_single_th_svm, n_windows)
statistics_level_5 = calculate_mean_and_confidence_interval(best_scores_level_5_single_th_svm, n_windows)
statistics_level_5_detail = calculate_mean_and_confidence_interval(best_scores_level_5_detail_th_svm, n_windows)

In [ ]:
'''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
#print(best_scores_level_4_single_th_svm['th_1']['0-50'])
#print(best_scores_level_4_single_th_svm['th_2']['0-50'])
#print(best_scores_level_4_single_th_svm['th_3']['0-50'])
#print()
#print(best_scores_level_4_single_th_svm['th_1']['25-75'])
#print(best_scores_level_4_single_th_svm['th_2']['25-75'])
#print(best_scores_level_4_single_th_svm['th_3']['25-75'])

In [ ]:
type(statistics_level_4)

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
!pwd

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('new_all_th_concat_reconstructions.pkl', 'rb') as f:
    new_all_th_concat_reconstructions = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_th['th_1'].keys()

In [ ]:
new_all_th_concat_reconstructions.keys()

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME '''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    subjects_dir = os.path.join(save_path, f'plot_mean_all_ths_level_{level}')
    os.makedirs(subjects_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 4:
        level_str = 'theta'
    elif level == 5:
        level_str = 'delta'
    elif level == '5_detail':
        level_str = 'theta_strict'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'all_ths_level_{level_str}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    print(f"\n\t\t\t\t\t\033[1mTherapists'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_th_concat_reconstructions.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    
    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)

    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Aggiunge il livello di baseline in base al livello specificato
    #if level == 4:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range')
    #elif level == 5:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range')
    #elif level == '5_detail':
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Detail Range')
    
    '''VECCHIO'''
    
    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
    if level_str == 'theta':
        ax1.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range', fontsize = 16)
        ax2.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range',  fontsize = 16)
        
    elif level_str == 'delta':
        ax1.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)
        ax2.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)

    elif level_str == 'theta_strict':
        ax1.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
        ax2.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
    
    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_ths_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(subjects_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_4, 4, save_path)
plot_mean_best_scores_for_window(statistics_level_5, 5, save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail, '5_detail', save_path)

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE E PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    

 # Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_all_th_concat_reconstructions_1_20.pkl', 'rb') as f:
    new_all_th_concat_reconstructions_1_20 = pickle.load(f)

In [ ]:
print(new_subject_level_concatenations_th_1_20.keys())
print()
print(new_subject_level_concatenations_th_1_20['th_1'].keys())
print(new_subject_level_concatenations_th_1_20['th_1']['data'].shape)
print()
print(new_all_th_concat_reconstructions_1_20.keys())
print(new_all_th_concat_reconstructions_1_20['data'].shape)

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''

import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_th = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'th_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_th:    
                best_scores_filtered_1_20_single_th[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_th[subject][window] = max(best_scores_filtered_1_20_single_th[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_th

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_th_svm = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_th_svm keys\033[0m: {best_scores_filtered_1_20_single_th_svm.keys()}")

for th_key, window_key in best_scores_filtered_1_20_single_th_svm.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        '''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")
    
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc = mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_1_20 = calculate_mean_and_confidence_interval(best_scores_filtered_1_20_single_th_svm, n_windows)

In [ ]:
'''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
#print(best_scores_level_4_single_th_svm['th_1']['0-50'])
#print(best_scores_level_4_single_th_svm['th_2']['0-50'])
#print(best_scores_level_4_single_th_svm['th_3']['0-50'])
#print()
#print(best_scores_level_4_single_th_svm['th_1']['25-75'])
#print(best_scores_level_4_single_th_svm['th_2']['25-75'])
#print(best_scores_level_4_single_th_svm['th_3']['25-75'])

In [ ]:
type(statistics_level_1_20)

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    data_dir = os.path.join(save_path, f'plot_mean_all_ths_level_{level}')
    os.makedirs(data_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 'filtered_1_20':
        level_str = 'filtered_1_20'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    #print(f"\n\t\t\t\t\t\033[1mPatients'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_th_concat_reconstructions_1_20.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}\n\n\n")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    
    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)
    
    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Linea orizzontale per il chance level
    #plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    #plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)')

    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è filtered_1_20, gestisci i titoli per i grafici su ax1 e ax2
    if level == 'filtered_1_20':

        ax1.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
        ax2.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
    
    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_ths_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(data_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'\nPlot salvato in: \n\033[1m{save_file_path}\033[0m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_1_20, 'filtered_1_20', save_path)

#### **ALL SINGLE PATIENTS (PT01-PT20)**

#### Automatization of all steps from: 

1) "**subject_level_concatenations_pt**" : ricostruzioni 4 e 5° livello wavelet da approx coefficients
2) "**new_subject_level_concatenations_pt**":  ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_pt_1_20**": EEG preprocessed signal filtered 1-20Hz 


In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)

##### **ALL SINGLE Patients (PT01-PT20) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DELLE RICOSTRUZIONI**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**

In [ ]:
''' SVM PATIENTS GIUSTA! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare


'''


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER SVM'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra il set di combinazioni tra gli iper-parametri, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...

'''

https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html


C-Support Vector Classification.
The implementation is based on libsvm. 
The fit time scales at least quadratically with the number of samples and may be impractical beyond tens of thousands of samples.

For large datasets consider using LinearSVC or SGDClassifier instead, possibly after a Nystroem transformer or other Kernel Approximation.

The multiclass support is handled according to a one-vs-one scheme.

For details on the precise mathematical formulation of 

-the provided kernel functions and 
-how gamma, coef0 and degree affect each other, 

see the corresponding section in the narrative documentation: Kernel functions.

To learn how to tune SVC’s hyperparameters, see the following example: Nested versus non-nested cross-validation

Read more in the User Guide.





# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)


Ad ora, la mia "valid_params_dict_svc" è fatta così:


valid_params_dict_svc = {
    'linear': [{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               {'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               ...], 
    'poly': [{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             {'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             ...], 
    'rbf': [...],
    'sigmoid': [...]
}



Ora, quindi, per accorpare tutti i dizionari contenuti nel tuo dizionario valid_params_dict_svc in un'unica lista di dizionari 
che può essere fornita a RandomizedSearchCV
devo iterare sulle chiavi principali del dizionario e 
concatenare le liste di iper-parametri per ciascun kernel in un'unica lista.

infatti --> https://scikit-learn.org/1.5/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

'params_distributions' dentro RandomizedSearchCV viene accettato come

- param_distributions: --> dict or list of dicts



# Crea una lista vuota per contenere tutti i parametri
all_params = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params.extend(params_list)



###CHECK PER PRINT VARI

# Ora all_params contiene tutti i dizionari concatenati
#print(f"all_params is:, {type(all_params)}")


# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in enumerate(all_params):
    print(params_list)
    
    
OUTPUT:

----

{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 10, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 100, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}

----

    
'''



# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)

# Crea una lista vuota per contenere tutti i parametri
all_params_svc = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params_svc.extend(params_list)
    
    
print(f"\t\t\t\033[1mAll Valid Testable Params will be among these below\033[0m:\n") 
for param_dict in all_params_svc: 
    
    #print(f"\033[1m{param_dict.keys()}\033[0m, {param_dict.values()}")
    
    print("{", end="")  # Inizia il dizionario
    for i, (key, value) in enumerate(param_dict.items()):
        
        # Formattazione della chiave in grassetto
        bold_key = f"\033[1m{key}\033[0m"
        
        # Se non è l'ultima coppia, aggiungi una virgola
        if i < len(param_dict) - 1:
            print(f"'{bold_key}': {value}, ", end="")
        else:
            print(f"'{bold_key}': {value}", end="")
    
    print("}")  # Chiude il dizionario e va a capo
    
# Itera attraverso i soggetti


'''OLD VERSION'''
#for subject, levels in subject_level_concatenations_th.items():


'''NEW VERSION'''
for subject, levels in new_subject_level_concatenations_pt.items():
    
    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO'''
    
    #if subject == 'pt_16':
    #if subject == 'pt_17' or subject == 'pt_18' or subject == 'pt_19':
    
    if subject == 'pt_20':
        
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")
        
        '''NEW VERSION'''
        #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
        params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params'

        # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
        #                                      'delta' = δ,i.e., approx_5 ,
        #                                      'theta_strict' = Θ, i.e., detail_5,
        #                                      'labels') 

        for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'


            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")

            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_std.txt'

            #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\t\033[1m{params_dir}\033[0m"),
            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

            y = levels['labels'] # Estraiamo le labels livello corrente del soggetto corrente

            print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


            #INIZIALIZZAZIONE XGBOOST'

            base_svc = SVC()

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            #invalid_combination_count = 0

            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_svc,
                        param_distributions = all_params_svc,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:


                        #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                        #calcolato sulla base di una cross-validation a 5 fold. 
                        #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                        #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                        #In sintesi, è il valore medio di accuracy ottenuto 
                        #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                        #per una specifica combinazione di iper-parametri!


                        for i, params in enumerate(rand_search.cv_results_['params']):
                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                #invalid_combination_count += 1
                                print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri
                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH
                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")
        

##### **ALL SINGLE Patients (PT01-PT15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

- **EEG preprocessed signal**: filtered 1-20

In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun soggetto nel dizionario
for soggetto, dati in new_subject_level_concatenations_pt_1_20.items():
    
    # Verifica che 'data' sia presente tra le chiavi
    if 'data' in dati:
        
        # Sotto-seleziona i canali di interesse
        dati_originali = dati['data']  # Estrai i dati
        
        dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali

        # Aggiorna la chiave 'data' con i dati filtrati
        new_subject_level_concatenations_pt_1_20[soggetto]['data'] = dati_sottoselezionati

        # Opzionale: stampa di controllo per verificare la nuova forma dei dati
        print(f"Soggetto {soggetto}: {dati_sottoselezionati.shape}")

In [ ]:
##### **ALL SINGLE Patients (PT01-PT15) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DAL SEGNALE 1-20Hz**


''' SVM GIUSTO! PAZIENTI NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare


'''


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER SVM'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra il set di combinazioni tra gli iper-parametri, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...

'''

https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html


C-Support Vector Classification.
The implementation is based on libsvm. 
The fit time scales at least quadratically with the number of samples and may be impractical beyond tens of thousands of samples.

For large datasets consider using LinearSVC or SGDClassifier instead, possibly after a Nystroem transformer or other Kernel Approximation.

The multiclass support is handled according to a one-vs-one scheme.

For details on the precise mathematical formulation of 

-the provided kernel functions and 
-how gamma, coef0 and degree affect each other, 

see the corresponding section in the narrative documentation: Kernel functions.

To learn how to tune SVC’s hyperparameters, see the following example: Nested versus non-nested cross-validation

Read more in the User Guide.





# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)


Ad ora, la mia "valid_params_dict_svc" è fatta così:


valid_params_dict_svc = {
    'linear': [{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               {'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               ...], 
    'poly': [{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             {'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             ...], 
    'rbf': [...],
    'sigmoid': [...]
}



Ora, quindi, per accorpare tutti i dizionari contenuti nel tuo dizionario valid_params_dict_svc in un'unica lista di dizionari 
che può essere fornita a RandomizedSearchCV
devo iterare sulle chiavi principali del dizionario e 
concatenare le liste di iper-parametri per ciascun kernel in un'unica lista.

infatti --> https://scikit-learn.org/1.5/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

'params_distributions' dentro RandomizedSearchCV viene accettato come

- param_distributions: dict or list of dicts



# Crea una lista vuota per contenere tutti i parametri
all_params = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params.extend(params_list)



###CHECK PER PRINT VARI

# Ora all_params contiene tutti i dizionari concatenati
#print(f"all_params is:, {type(all_params)}")


# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in enumerate(all_params):
    print(params_list)
    
    
OUTPUT:

----

{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 10, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 100, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}

----

    
'''



# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)

# Crea una lista vuota per contenere tutti i parametri
all_params_svc = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params_svc.extend(params_list)
    
    
print(f"\t\t\t\033[1mAll Valid Testable Params will be among these below\033[0m:\n") 
for param_dict in all_params_svc: 
    
    #print(f"\033[1m{param_dict.keys()}\033[0m, {param_dict.values()}")
    
    print("{", end="")  # Inizia il dizionario
    for i, (key, value) in enumerate(param_dict.items()):
        # Formattazione della chiave in grassetto
        bold_key = f"\033[1m{key}\033[0m"
        
        # Se non è l'ultima coppia, aggiungi una virgola
        if i < len(param_dict) - 1:
            print(f"'{bold_key}': {value}, ", end="")
        else:
            print(f"'{bold_key}': {value}", end="")
    
    print("}")  # Chiude il dizionario e va a capo
    

# Itera attraverso i soggetti
#for subject, levels in subject_level_concatenations_pt_1_20.items():

for subject, subj_dict in new_subject_level_concatenations_pt_1_20.items():
    
    '''TOGLI L'IF STATEMENT if subject == '...': E INDENTA INDIETRO SE VUOI PRENDERE TUTTI I DATI DI OGNI SINGOLO SOGGETTO'''
    
    #if subject == 'pt_16':
    #if subject == 'pt_17' or subject == 'pt_18' or subject == 'pt_19':
    
    #if subject == 'pt_20':
        
    print(f"\n\nCurrent Subject \033[1m{subject}\033[0m")

    print(f"\n\n\033[1mExtraction of Data\033[0m from Subject \033[1m{subject}\033[0m from Original Filtered Signal in \033[1m1-20Hz\033[0m")

    X = subj_dict['data'] # Estraiamo i dati del soggetto corrente

    y = subj_dict['labels'] # Estraiamo le labels livello corrente del soggetto corrente

    #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
    params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20'

    #FILE PATH DINAMICA PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
    #A SECONDA DEL SOGGETTO E LIVELLO DI RICOSTRUZIONE DEI DATI PRESI IN ESAME 

    # Costruzione del percorso del file in maniera dinamica
    params_file_path = f'{params_dir}/optimized_params_{subject}_filtered_1_20_std.txt'

    if not os.path.exists(params_dir):
        os.makedirs(params_dir)

    #print(f"\n\t\t\t\t\tCARTELLA CREATA ALLA DIRECTORY:\n\033[1m{params_dir}\033[0m"),
    #print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m, \n\033[1m{params_file_path}\033[0m\n")

    #Path per combinazioni iperparametri NON valide
    #invalid_params_file_path = f'{params_dir}/invalid_params_{subject}_filtered_1_20_std.txt'

    print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m: {X.shape}")

    y = y.astype(int) 

    print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m: {y.shape}")


    # Calcola il numero totale di etichette livello 4/5°
    label_counts = np.unique(y, return_counts = True)[1]
    total_labels = len(y)

    # Calcola la percentuale di ciascuna classe
    class_proportions = label_counts / total_labels * 100

    print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

    # Calcola i pesi delle classi come l'inverso delle proporzioni
    class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

    # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
    class_weights /= class_weights.sum()

    print(f"\n\033[1mClass Weights {class_weights}\033[0m")

    # Crea un dizionario per class_weight
    class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}

    '''INIZIALIZZAZIONE XGBOOST'''

    base_svc = SVC()

    # Memorizza il tempo di inizio
    start_time = time.time()

    # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
    execution_times = []

    # Contatori per combinazioni valide e non valide
    valid_combination_count = 0
    invalid_combination_count = 0

    # File di output per i parametri ottimizzati
    with open(params_file_path, 'w') as f:
        f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

    # File di output per i parametri ottimizzati NON validi
    #with open(invalid_params_file_path, 'w') as invalid_f:
    #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


    '''INIZIALIZZAZIONE RANDOM SEARCH'''

    # Lista per memorizzare i risultati delle finestre
    window_results = []

    # Creazione della finestra scorrevole con step e dimensioni desiderate
    n_samples = X.shape[2]
    window_size = 50
    step_size = 25
    n_windows = (n_samples - window_size) // step_size + 1


    #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

    # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

    for window_start in range(0, n_samples - window_size + 1, step_size):

        # Memorizza il tempo di inizio per il punto temporale corrente
        time_point_start = time.time()

        # Definiamo la finestra corrente
        window_end = window_start + window_size

        print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

        X_window = X[:, :, window_start:window_end]
        #print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

        # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
        X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
        #print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

        # Standardizza i dati della finestra corrente
        scaler = StandardScaler()
        X_window_standardized = scaler.fit_transform(X_window_reshaped)
        #print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

        try:
            print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


            rand_search = RandomizedSearchCV(
                estimator = base_svc,
                param_distributions = all_params_svc,
                scoring ='accuracy',
                n_iter = 100,
                verbose = 1,
                n_jobs = -1
            )


            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

            # Esegui RandomizedSearchCV sulla finestra corrente
            rand_search.fit(X_window_standardized, y)


            # Controlla il numero totale di combinazioni testate
            total_combinations_tested = len(rand_search.cv_results_['params'])
            #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

            # Salva tutte le combinazioni testate per la finestra corrente
            with open(params_file_path, 'a') as f:

                '''
                Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                calcolato sulla base di una cross-validation a 5 fold. 
                Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                In sintesi, è il valore medio di accuracy ottenuto 
                mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                per una specifica combinazione di iper-parametri!
                '''

                for i, params in enumerate(rand_search.cv_results_['params']):
                    score = rand_search.cv_results_['mean_test_score'][i]
                    f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                for params in rand_search.cv_results_['params']:
                    if params:
                        valid_combination_count += 1
                    else:
                        invalid_combination_count += 1
                        print(f"Invalid combination found: {params}")

                #QUI

                # Ottieni il modello con i migliori iper-parametri
                best_model_params = rand_search.best_params_


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH
                best_score = rand_search.best_score_


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                # Memorizza i risultati della finestra corrente
                window_results.append({
                    'window_start': window_start,
                    'window_end': window_end,
                    'best_params': best_model_params,
                    'best_score': best_score
                })


                #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

            #Salva i parametri migliori per la finestra corrente in una riga del file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                f.write('\n')

        except Exception as e:

            print(f'Error: {e}')

            # Scrivi la combinazione non valida nel file di output
            #with open(invalid_params_file_path, 'a') as invalid_f:
            #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
            #continue


            # Memorizza il tempo di fine per il punto temporale corrente
            time_point_end = time.time()

            # Calcola il tempo di esecuzione per il punto temporale corrente
            time_point_elapsed = time_point_end - time_point_start

            # Aggiungi il tempo di esecuzione alla lista
            execution_times.append(time_point_elapsed)

            # Stampa i risultati per il punto temporale corrente
            #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
            #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
            #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
            #print()
            #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
            #print()

    # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

    # Definisci il range generale delle finestre che vuoi analizzare
    general_range = [0, 300]  # Puoi modificare il range se necessario

    # Filtra i risultati delle finestre nel range desiderato
    general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

    # Controlla se ci sono risultati validi all'interno del range specificato
    if general_results:

        # Trova la finestra con il punteggio migliore
        best_general_window = max(general_results, key=lambda x: x['best_score'])

        # Trova i parametri migliori per questa finestra specifica (se disponibili)
        best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
        best_general_window['best_params'] = best_params

        # Stampa le informazioni sulla finestra migliore trovata
        #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
        #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
        #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

    else:
        print("No valid windows found in the specified range.")


    # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
    window_results.append({
        'Best window_start': best_general_window['window_start'] if general_results else None,
        'Best window_end': best_general_window['window_end'] if general_results else None,
        'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
        'best_score': best_general_window['best_score'] if general_results else None
    })

    # Calcola il tempo di esecuzione totale
    end_time = time.time()
    total_execution_time = end_time - start_time

    #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
    #print()
    #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
    #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

    # Aggiungi il risultato della migliore finestra generale al file di testo
    with open(params_file_path, 'a') as f:
        f.write('\n')
        if general_results:
            best_general_window = max(general_results, key=lambda x: x['best_score'])
            f.write(f"BEST WINDOW OVERALL: "),
            f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
            f.write(f"\nBest Window End: {best_general_window['window_end']}"),
            f.write(f"\nBest Score: {best_general_window['best_score']}")

            if best_general_window['best_params'] is not None:
                    f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
            else:
                f.write("No valid windows found in the specified range.\n")

            f.write('\n')
            f.write(f"Total execution time: {total_execution_time} seconds\n")
            f.write(f"Number of valid combinations: {valid_combination_count}\n")
            f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")

#### **ALL SINGLE Patients (PT01-PT20) for **COUPLED EXPERIMENTAL CONDITIONS****

#### Automatization of all steps from: 

1) "**new_subject_level_concatenations_coupled_exp_pt**" ricostruzioni 4 e 5° livello wavelet da approx coefficients + 5° livello wavelet da detail coefficients 
3) "**new_subject_level_concatenations_coupled_exp_pt_1_20**": EEG preprocessed signal filtered 1-20Hz 

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''OLD --> cd '/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE'''


#import pickle

# Caricare l'intero dizionario annidato con pickle
#with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
#    new_subject_level_concatenations_th = pickle.load(f)
    
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle
import numpy as np


base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'

#f'{base_dir}/

with open(f'{base_dir}/new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open(f'{base_dir}/new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open(f'{base_dir}/new_subject_level_concatenations_coupled_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open(f'{base_dir}/new_subject_level_concatenations_coupled_exp_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt_1_20 = pickle.load(f)
    
    
    
#PER SALVARE I FILE
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#import pickle
# Salvare l'intero dizionario annidato con pickle
#with open('NOME DEL FILE.pkl', 'wb') as f:
#    pickle.dump(subject_level_concatenations, f)


#subject_level_concatenations_th['th_1'].keys()

In [ ]:
print(f"\t\t\tDataset Organization: \033[new_subject_level_concatenations_coupled_exp_pt\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt['pt_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp'].keys()}")

In [ ]:
np.unique(new_subject_level_concatenations_coupled_exp_pt['pt_20']['theta']['baseline_vs_th_resp']['labels'],return_counts=True)

##### **Descrizione degli step nel codice per ottenere e salvare nelle paths le best score performances per il level 4 e 5 dalle ricostruzioni**:

Vorrei in questo caso, per velocizzare, iterare su 

subject_level_concatenations, che ha questa struttura...

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


al cui interno ha per ogni chiave di primo ordine, un altro dizionario annidato, che è fatto di queste chiavi


dict_keys(['theta', 'delta', 'labels'])

dentro 'theta' e 'delta' ci sono tutti i dati di tutte le condizioni sperimentali del singolo soggetto

del tipo 'theta' o 'delta' conterrà un array con shape

(204, 3, 300)

con 1° dimensione i trial, poi i canali, poi i punti di ogni trial (campioni EEG)

e dentro 'labels' ho invece l'array delle labels concatenate...
(204,)


<br>


Ora però, vorrei che ... 

Se ad esempio nel soggetto 'th_1' entri nella chiave 'theta', 

allora poi il file corrispondente .txt deve essere scritto con una path dinamica, che cambia a seconda 
- sia del soggetto iterato
- sia del livello di ricostruzione dei dati

Ossia:

la "params_dir" è fissa

mentre 

"params_file_path" è dinamica, e cambia a seconda del soggetto iterato e del livello. 

Per cui sarà una composizione di stringhe fisse e stringhe 'mobili', ossia

'params_file_path' = 'optimized_params_' + {subject} dove subject dovrebbe essere una lista di stringhe che si preleva dalle chiavi di primo ordine di "subject_level_concatenations" che erano

dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])


seguito da "_level_{level}_std" dove {level} dipende dal nome della chiave del sotto-dizionario iterato per ogni soggetto...

Ossia, ad esempio dentro il sotto-dizionario del primo soggetto di "subject_level_concatenations" cioè

subject_level_concatenations['th_1'], 

Se la sua sotto-chiave è 'theta' allora il level = 4, se la chiave è 'delta' allora il level = 5, 



Quindi la costruzione finale della path dinamica del file specifico per il soggetto 1 deve essere

 
params_file_path = 'optimized_params_' +'{subject}' + "_level_{level}_std.txt"

e sarà se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_1' + "_level_4_std.txt"


e sarà se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_1' + "_level_5_std.txt"


in questo modo, farei un loop unico su tutte le sottochiavi dei dizionari annidati dentro 
"subject_level_concatenations" 

ossia 
dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15'])

e per ognuno vedo se la sua sotto-chiave sarà 'theta' o 'delta' e creerà dei file .txt corrispondenti nella param_dir che gli ho chiesto...

Il resto del codice non toccarlo invece, perché dovrebbe creare dei file .txt per ogni soggetto per ogni livello di ricostruzione dei dati,
e salverà le analisi nel file .txt corrispondente



Ad esempio, continuando col soggetto 2:

la costruzione finale della path dinamica del file specifico per il soggetto 2

Sarà, se entri dentro la sottochiave 'theta':

params_file_path = 'optimized_params_' +'th_2' + "_level_4_std.txt"


e sarà, se entri dentro la sottochiave 'delta':

params_file_path = 'optimized_params_' +'th_2' + "_level_5_std.txt"


e così via per tutti gli altri soggetti




##### **ALL SINGLE Patients (PT01-PT20) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DALLE RICOSTRUZIONI** 

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **4° livello Approx coefficients: Θ+δ range**
- **5° livello Approx coefficients: δ range**
- **5° livello detail coefficients: Θ range**


###### **ISTRUZIONI PER MODIFICHE AL CASO 2 CLASSI**

Allora, andiamo per step:

**1)** la nuova variabile sulla quale iterare è new_subject_level_concatenations_coupled_exp_th

che è fatta con questa struttura

print(f"\t\t\tDataset Organization: \033[1mnew_subject_level_concatenations_coupled_exp_th\033[0m")
print(f"\n\033[1mFirst Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th.keys()}")
print()
print(f"\033[1mSecond Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1'].keys()}")
print()
print(f"\033[1mThird Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys()}")
print()
print(f"\033[1mFourth Order Key\033[0m: {new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys()}")

OUTPUT:

Dataset Organization: new_subject_level_concatenations_coupled_exp_th

First Order Key: dict_keys(['th_1', 'th_2', 'th_3', 'th_4', 'th_5', 'th_6', 'th_7', 'th_8', 'th_9', 'th_10', 'th_11', 'th_12', 'th_13', 'th_14', 'th_15', 'th_16'])

Second Order Key: dict_keys(['theta', 'delta', 'theta_strict'])

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

Fourth Order Key: dict_keys(['data', 'labels'])

quindi significa che, per ogni soggetto, tu dovrai entrare nella sotto sotto chiave relativa ai livelli di ricostruzione del segnale 

dict_keys(['theta', 'delta', 'theta_strict'])

per ognuna di queste, avrai appunto delle altre sotto-sotto-sotto chiavi, che sono le condizioni sperimentali, sulle quali dovrai entrare che sono 

Third Order Key: dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])

dopodiché dentro ognuna di queste, dovrai entrare ulteriormente dentro ciascuna sotto chiave di quarto livello:

la prima, che fa riferimento ai dati('data') il cui valore (array numpy() verrà assegnato ad X nel codice, e 
la seconda, la chiave delle labels ('labels') il cui valore verrà assegnato ad Y...

**2)** questa parte relativa ai print

 for level_key, data in levels.items():

            if level_key == 'theta':

                level = "approx_4"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello theta del soggetto corrente


            elif level_key == 'delta':

                level = "approx_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente


            elif level_key == 'theta_strict':
                #continue  # Ignora se non è 'theta' o 'delta'

                level = "detail_5"

                print(f"\n\033[1mExtraction of Data\033[0m from  Subject \033[1m{subject}\033[0m from Level \033[1m{level_key}\033[0m")

                X = data  # Estraiamo i dati del livello delta del soggetto corrente

            else:
                continue # Saltiamo il livello se non è 'theta', 'delta' o 'theta_strict'

voglio che poi abbia degli altri if, nel senso che vorrei che iterando su ogni livello, voglio che venga applicata la stessa logica dei printing di qui sopra, ma alle chiavi del 3° livello, ossia quelle che fanno riferimento alle condizioni sperimentali...

ossia, 

voglio che ci sia scritto per le X

print(f"\n\033[1mExtraction of Data\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

e voglio che ci sia scritto per le Y

print(f"\n\033[1mExtraction of Labels\033[0m - Condition {experimental_condition}  from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")  

dove 

"experimental_condition" farà riferimento alla chiave della condizione sperimentale iterata in quel loop, e 

"level_key" invece farà riferimento alle chiavi del 2° livello, ossia a quelle che si riferiscono allo specifico livello di ricostruzione del segnale per il quale io sto estraendo i dati e le labels al ciclo corrente...

In questo modo, dovrei avere un'idea dai print del mio codice, quando viene eseguito, su quale soggetto, quale livello e quale condizione sperimentale sta eseguendo i calcoli.. 

**3)** voglio che vengano create dei folder nuovi per appendere i risultati di tutte le elaborazioni da parte dei vari modelli e che saranno queste due cartelle

"EEG_50_window_25_overlap_coupled_exp_cond" 
"single_therapist_optimized_params_coupled_exp_cond"
 
ossia la mia directory dovrebbe diventare

params_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond'

per cui, se "EEG_50_window_25_overlap_coupled_exp_cond" né "single_therapist_optimized_params_coupled_exp_cond" non sono state create, allora andranno create...

**4)** la creazione del nome del file relativo ad un determinato soggetto dovrà essere formato in questo modo

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

dove, ricorda, "experimental_condition" farà riferimento alle insieme delle stringhe che compongono la chiave della condizione sperimentale iterata in quel loop (chiavi di 3° livello di "new_subject_level_concatenations_coupled_exp_th" 

del tipo potrebbe essere

**Costruzione del percorso del file in maniera dinamica**
            params_file_path = f'{params_dir}/optimized_params_{subject}_level_{level}_{experimental_condition}_std.txt'

Con ad esempio:

subject = th_1
level = theta 
experimental_condition = baseline_vs_th_resp

per cui sarebbe 

f'{params_dir}/optimized_params_th_1_level_theta_baseline_vs_th_resp_std.txt'

**5)** al momento, il settaggio degli iper-parametri è impostato per anche per i casi multi-nomiali ma in questo caso il codice verrà usato per task di classificazione binaria...

per cui, voglio essere sicuro che l'impostazione attuale vada anche bene per i casi semplicemente binomiali, ossia di due possibili classi solo...

per farlo, ti do il link della pagina della Logistic Regression, in modo che tu mi dica se l'attuale implementazione sia corretta....

https://scikit-learn.org/1.5/modules/generated/sklearn.linear_model.LogisticRegression.html


**6)** Fai le modifiche a quello che ti ho chiesto, non azzardare cose in più od in meno, vorrei che ti attenessi a ciò che ti ho chiesto...


##### **IMPLEMENTATION SVM FOR COUPLED EXPERIMENTAL CONDITIONS**

In [ ]:
new_subject_level_concatenations_coupled_exp_pt['pt_20']['theta']['baseline_vs_th_resp'].keys()

In [ ]:
''' SVM GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare


'''


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER SVM'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra il set di combinazioni tra gli iper-parametri, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...

'''

https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html


C-Support Vector Classification.
The implementation is based on libsvm. 
The fit time scales at least quadratically with the number of samples and may be impractical beyond tens of thousands of samples.

For large datasets consider using LinearSVC or SGDClassifier instead, possibly after a Nystroem transformer or other Kernel Approximation.

The multiclass support is handled according to a one-vs-one scheme.

For details on the precise mathematical formulation of 

-the provided kernel functions and 
-how gamma, coef0 and degree affect each other, 

see the corresponding section in the narrative documentation: Kernel functions.

To learn how to tune SVC’s hyperparameters, see the following example: Nested versus non-nested cross-validation

Read more in the User Guide.





# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)


Ad ora, la mia "valid_params_dict_svc" è fatta così:


valid_params_dict_svc = {
    'linear': [{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               {'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               ...], 
    'poly': [{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             {'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             ...], 
    'rbf': [...],
    'sigmoid': [...]
}



Ora, quindi, per accorpare tutti i dizionari contenuti nel tuo dizionario valid_params_dict_svc in un'unica lista di dizionari 
che può essere fornita a RandomizedSearchCV
devo iterare sulle chiavi principali del dizionario e 
concatenare le liste di iper-parametri per ciascun kernel in un'unica lista.

infatti --> https://scikit-learn.org/1.5/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

'params_distributions' dentro RandomizedSearchCV viene accettato come

- param_distributions: dict or list of dicts



# Crea una lista vuota per contenere tutti i parametri
all_params = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params.extend(params_list)



###CHECK PER PRINT VARI

# Ora all_params contiene tutti i dizionari concatenati
#print(f"all_params is:, {type(all_params)}")


# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in enumerate(all_params):
    print(params_list)
    
    
OUTPUT:

----

{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 10, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 100, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}

----

    
'''


# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)

# Crea una lista vuota per contenere tutti i parametri
all_params_svc = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params_svc.extend(params_list)
    
    
print(f"\t\t\t\033[1mAll Valid Testable Params will be among these below\033[0m:\n") 
for param_dict in all_params_svc: 
    
    #print(f"\033[1m{param_dict.keys()}\033[0m, {param_dict.values()}")
    
    print("{", end="")  # Inizia il dizionario
    for i, (key, value) in enumerate(param_dict.items()):
        # Formattazione della chiave in grassetto
        bold_key = f"\033[1m{key}\033[0m"
        
        # Se non è l'ultima coppia, aggiungi una virgola
        if i < len(param_dict) - 1:
            print(f"'{bold_key}': {value}, ", end="")
        else:
            print(f"'{bold_key}': {value}", end="")
    
    print("}")  # Chiude il dizionario e va a capo
    
# Itera attraverso i soggetti

'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_patient_optimized_params_coupled_exp_cond"

# Iterazione sulla struttura `new_subject_level_concatenations_coupled_exp_pt`

for subject, levels in new_subject_level_concatenations_coupled_exp_pt.items():
    
    #if subject == 'pt_1':
    #if subject == 'pt_17' or subject == 'pt_18' or subject == 'pt_19':
    
    if subject == 'pt_3':
        
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {subject}\033[0m\n\n")

        for level_key, experimental_condition in levels.items():

            # Itera attraverso le chiavi annidate ('theta' = Θ, i.e., approx_4, 
            #                                      'delta' = δ,i.e., approx_5 ,
            #                                      'theta_strict' = Θ, i.e., detail_5,
            #                                      'labels') 

            # Identificazione del livello
            if level_key == 'theta':
                level = "approx_4"


            elif level_key == 'delta':
                level = "approx_5"


            elif level_key == 'theta_strict':
                level = "detail_5"

            else:
                continue  # Ignora livelli non rilevanti


            print(f"\nProcessing Data \033[1m from Level: \033[1m{level_key}\033[0m for Subject \033[1m{subject}\033[0m")

            for condition, data_dict in experimental_condition.items():

                # Estrazione dei dati e delle label
                X = data_dict['data'] # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente

                # Messaggi di log per dati e label
                print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

                print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{subject}\033[0m by the Level \033[1m{level_key}\033[0m")

                y = data_dict['labels'] # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente


                '''NEW VERSION'''
                #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
                params_dir = params_dir

                # Creazione della cartella, se non esiste
                if not os.path.exists(params_dir):
                    os.makedirs(params_dir)
                    print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


                # Costruzione del percorso del file in maniera dinamica
                params_file_path = f"{params_dir}/optimized_params_{subject}_level_{level}_{condition}_std.txt"

                print(f"\n\nPATHFILE PER SOGGETTO \033[1m{subject}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")
                print(f"\033[1m{params_file_path}\033[0m\n")

                print(f"\n\033[1mShape of data\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

                y = y.astype(int) 

                print(f"\n\033[1mShape of labels\033[0m for \033[1m{subject}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


                # Calcola il numero totale di etichette livello 4/5°
                label_counts = np.unique(y, return_counts = True)[1]
                total_labels = len(y)

                # Calcola la percentuale di ciascuna classe
                class_proportions = label_counts / total_labels * 100

                print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

                # Calcola i pesi delle classi come l'inverso delle proporzioni
                class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

                # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
                class_weights /= class_weights.sum()

                print(f"\n\033[1mClass Weights {class_weights}\033[0m")

                # Crea un dizionario per class_weight
                class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}


                #INIZIALIZZAZIONE SVC

                base_svc = SVC()

                # Memorizza il tempo di inizio
                start_time = time.time()

                # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
                execution_times = []

                # Contatori per combinazioni valide e non valide
                valid_combination_count = 0
                invalid_combination_count = 0

                # File di output per i parametri ottimizzati
                with open(params_file_path, 'w') as f:
                    f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

                # File di output per i parametri ottimizzati NON validi
                #with open(invalid_params_file_path, 'w') as invalid_f:
                #    invalid_f.write(f"Invalid Parameter Combinations\n\n")



                #INIZIALIZZAZIONE RANDOM SEARCH

                # Lista per memorizzare i risultati delle finestre
                window_results = []

                # Creazione della finestra scorrevole con step e dimensioni desiderate
                n_samples = X.shape[2]
                window_size = 50
                step_size = 25
                n_windows = (n_samples - window_size) // step_size + 1


                #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

                # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

                for window_start in range(0, n_samples - window_size + 1, step_size):

                    # Memorizza il tempo di inizio per il punto temporale corrente
                    time_point_start = time.time()

                    # Definiamo la finestra corrente
                    window_end = window_start + window_size

                    print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                    X_window = X[:, :, window_start:window_end]
                    print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                    # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                    X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                    print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                    # Standardizza i dati della finestra corrente
                    scaler = StandardScaler()
                    X_window_standardized = scaler.fit_transform(X_window_reshaped)
                    print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                    try:
                        print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                        rand_search = RandomizedSearchCV(
                            estimator = base_svc,
                            param_distributions = all_params_svc,
                            scoring ='accuracy',
                            n_iter = 100,
                            verbose = 1,
                            n_jobs = -1
                        )


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Esegui RandomizedSearchCV sulla finestra corrente
                        rand_search.fit(X_window_standardized, y)


                        # Controlla il numero totale di combinazioni testate
                        total_combinations_tested = len(rand_search.cv_results_['params'])
                        #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                        # Salva tutte le combinazioni testate per la finestra corrente
                        with open(params_file_path, 'a') as f:


                            #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                            #calcolato sulla base di una cross-validation a 5 fold. 
                            #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                            #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                            #In sintesi, è il valore medio di accuracy ottenuto 
                            #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                            #per una specifica combinazione di iper-parametri!


                            for i, params in enumerate(rand_search.cv_results_['params']):
                                score = rand_search.cv_results_['mean_test_score'][i]
                                f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                            for params in rand_search.cv_results_['params']:
                                if params:
                                    valid_combination_count += 1
                                else:
                                    #invalid_combination_count += 1
                                    print(f"Invalid combination found: {params}")

                            #QUI

                            # Ottieni il modello con i migliori iper-parametri
                            best_model_params = rand_search.best_params_


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH
                            best_score = rand_search.best_score_


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                            # Memorizza i risultati della finestra corrente
                            window_results.append({
                                'window_start': window_start,
                                'window_end': window_end,
                                'best_params': best_model_params,
                                'best_score': best_score
                            })


                            #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                        with open(params_file_path, 'a') as f:
                            f.write('\n')
                            f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                            f.write('\n')

                    except Exception as e:

                        print(f'Error: {e}')

                        # Scrivi la combinazione non valida nel file di output
                        #with open(invalid_params_file_path, 'a') as invalid_f:
                        #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                        #continue


                        # Memorizza il tempo di fine per il punto temporale corrente
                        time_point_end = time.time()

                        # Calcola il tempo di esecuzione per il punto temporale corrente
                        time_point_elapsed = time_point_end - time_point_start

                        # Aggiungi il tempo di esecuzione alla lista
                        execution_times.append(time_point_elapsed)

                        # Stampa i risultati per il punto temporale corrente
                        #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                        #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                        #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                        #print()
                        #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                        #print()

                # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

                # Definisci il range generale delle finestre che vuoi analizzare
                general_range = [0, 300]  # Puoi modificare il range se necessario

                # Filtra i risultati delle finestre nel range desiderato
                general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

                # Controlla se ci sono risultati validi all'interno del range specificato
                if general_results:

                    # Trova la finestra con il punteggio migliore
                    best_general_window = max(general_results, key=lambda x: x['best_score'])

                    # Trova i parametri migliori per questa finestra specifica (se disponibili)
                    best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                    best_general_window['best_params'] = best_params

                    # Stampa le informazioni sulla finestra migliore trovata
                    #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                    #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                    #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

                else:
                    print("No valid windows found in the specified range.")


                # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
                window_results.append({
                    'Best window_start': best_general_window['window_start'] if general_results else None,
                    'Best window_end': best_general_window['window_end'] if general_results else None,
                    'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                    'best_score': best_general_window['best_score'] if general_results else None
                })

                # Calcola il tempo di esecuzione totale
                end_time = time.time()
                total_execution_time = end_time - start_time

                #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
                #print()
                #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
                #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

                # Aggiungi il risultato della migliore finestra generale al file di testo
                with open(params_file_path, 'a') as f:
                    f.write('\n')
                    if general_results:
                        best_general_window = max(general_results, key=lambda x: x['best_score'])
                        f.write(f"BEST WINDOW OVERALL: "),
                        f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                        f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                        f.write(f"\nBest Score: {best_general_window['best_score']}")

                        if best_general_window['best_params'] is not None:
                                f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                        else:
                            f.write("No valid windows found in the specified range.\n")

                        f.write('\n')
                        f.write(f"Total execution time: {total_execution_time} seconds\n")
                        f.write(f"Number of valid combinations: {valid_combination_count}\n")
                        f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")
    

##### **ALL SINGLE Patients (PT01-PT16) CODE PER CALCOLO E SALVATAGGIO BEST PERFORMANCES DA**

##### **COUPLED EXPERIMENTAL CONDITIONS**

- **EEG preprocessed signal**: filtered 1-20

In [ ]:
#new_subject_level_concatenations_pt_1_20.keys()
#new_subject_level_concatenations_pt_1_20['pt_1'].keys()

#new_subject_level_concatenations_coupled_exp_pt.keys()

#new_subject_level_concatenations_coupled_exp_pt_1_20.keys()
#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1'].keys()


#new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp'].keys()

In [ ]:
import pickle
import numpy as np


with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    
    
# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt = pickle.load(f)


# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt_1_20 = pickle.load(f)

In [ ]:
# Definisci gli indici dei canali di interesse
canali_di_interesse = [12, 30, 48]  # Indici dei canali Fz_1, Cz_1, Pz_1

# Itera su ciascun livello temporale (th_1, th_2, ..., th_16)
for id_subj in new_subject_level_concatenations_coupled_exp_pt_1_20.keys():
    
    # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
    for exp_cond in new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj].keys():
        
        # Verifica che 'data' sia presente tra le chiavi della condizione
        if 'data' in new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj][exp_cond]:
            
            # Estrai i dati originali
            dati_originali = new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj][exp_cond]['data']
            
            # Sotto-seleziona i canali di interesse
            dati_sottoselezionati = dati_originali[:, canali_di_interesse, :]  # Sotto-seleziona i canali
            
            # Aggiorna la chiave 'data' con i dati filtrati
            new_subject_level_concatenations_coupled_exp_pt_1_20[id_subj][exp_cond]['data'] = dati_sottoselezionati

            # Opzionale: stampa di controllo per verificare la nuova forma dei dati
            print(f"Subj \033[1m{id_subj}\033[0m, Condizione \033[1m{exp_cond}\033[0m: {dati_sottoselezionati.shape}")

In [ ]:
new_subject_level_concatenations_coupled_exp_pt_1_20.keys()
np.shape(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp']['data'])

In [ ]:
''' SVM GIUSTO! NON TOCCARE

CODICE PER TUTTI I SOGGETTI PER OGNI LIVELLO DI RICOSTRUZIONE DEL SEGNALE (i.e., δ e Θ)

Il parametro n_iter nella RandomizedSearchCV specifica il numero di iterazioni da eseguire durante la ricerca casuale 
per trovare le migliori combinazioni di iperparametri. 

Quando imposti n_iter = 20, come nel tuo caso, stai dicendo al modello di esplorare casualmente 20 combinazioni 
diverse di iperparametri dal dizionario param_distributions.

Quando la ricerca è completata, RandomizedSearchCV restituirà la migliore combinazione di parametri trovata tra quelle testate, 
basata sulla metrica di valutazione specificata (nel tuo caso, scoring='accuracy'). 

Anche se hai impostato n_iter = 200, se RandomizedSearchCV trova una combinazione che ottiene risultati soddisfacenti 
tra le prime 20 iterazioni, non continuerà a cercare per le restanti 180 iterazioni. 
Questo è perché la ricerca casuale non esplora in modo sistematico tutte le possibili combinazioni, 
ma piuttosto si ferma dopo aver testato un numero fisso di iterazioni specificato da n_iter.


# Definizione dello spazio degli iperparametri da esplorare


'''


'''DEFINIZIONE COMBINAZIONI IPER-PARAMETRI VALIDE PER SVM'''

# Creazione di una lista di combinazioni valide di iperparametri!
# Filtro delle combinazioni di iperparametri valide per il caso multinomiale
# Questa parte serve per 'filtrare' il set di combinazione realmente possibili 
# tra il set di combinazioni tra gli iper-parametri, 
# da cui pescare poi successivamente in maniera casuale dalla Random Search...

'''

https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html


C-Support Vector Classification.
The implementation is based on libsvm. 
The fit time scales at least quadratically with the number of samples and may be impractical beyond tens of thousands of samples.

For large datasets consider using LinearSVC or SGDClassifier instead, possibly after a Nystroem transformer or other Kernel Approximation.

The multiclass support is handled according to a one-vs-one scheme.

For details on the precise mathematical formulation of 

-the provided kernel functions and 
-how gamma, coef0 and degree affect each other, 

see the corresponding section in the narrative documentation: Kernel functions.

To learn how to tune SVC’s hyperparameters, see the following example: Nested versus non-nested cross-validation

Read more in the User Guide.





# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)


Ad ora, la mia "valid_params_dict_svc" è fatta così:


valid_params_dict_svc = {
    'linear': [{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               {'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}, 
               ...], 
    'poly': [{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             {'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}, 
             ...], 
    'rbf': [...],
    'sigmoid': [...]
}



Ora, quindi, per accorpare tutti i dizionari contenuti nel tuo dizionario valid_params_dict_svc in un'unica lista di dizionari 
che può essere fornita a RandomizedSearchCV
devo iterare sulle chiavi principali del dizionario e 
concatenare le liste di iper-parametri per ciascun kernel in un'unica lista.

infatti --> https://scikit-learn.org/1.5/modules/generated/sklearn.model_selection.RandomizedSearchCV.html

'params_distributions' dentro RandomizedSearchCV viene accettato come

- param_distributions: dict or list of dicts



# Crea una lista vuota per contenere tutti i parametri
all_params = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params.extend(params_list)



###CHECK PER PRINT VARI

# Ora all_params contiene tutti i dizionari concatenati
#print(f"all_params is:, {type(all_params)}")


# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in enumerate(all_params):
    print(params_list)
    
    
OUTPUT:

----

{'kernel': 'linear', 'C': 0.001, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.01, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 0.1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 1, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 10, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'linear', 'C': 100, 'gamma': None, 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.001, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.01, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 0.1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 1, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 10, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'scale', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'poly', 'C': 100, 'gamma': 'auto', 'degree': 2, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'rbf', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.001, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.01, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 0.1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 1, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 10, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'scale', 'degree': None, 'class_weight': 'balanced'}
{'kernel': 'sigmoid', 'C': 100, 'gamma': 'auto', 'degree': None, 'class_weight': 'balanced'}

----

    
'''



# Definizione dei parametri validi per sklearn.svm.SVC
# Definizione dei parametri validi per SVC

import numpy as np

import time
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
import joblib

import json
import os

from sklearn.preprocessing import StandardScaler

from sklearn.svm import SVC


# Definizione aggiornata dei parametri validi per SVC
params_svc = {
    'kernel': [['linear'], ['poly'], ['rbf'], ['sigmoid']],  # Parametro kernel come lista di liste
    'C': [0.001, 0.01, 0.1, 1, 10, 100],  # Parametro C con valori su scala logaritmica
    'gamma': ['scale', 'auto'],  # Gamma può essere 'scale', 'auto' (o valori numerici) per kernel 'rbf’, ‘poly’ e ‘sigmoid’.
    'degree': [2],  # Degree per kernel polinomiale è fisso a 2
    'class_weight': ['balanced']  # Usa solo 'balanced' per il peso delle classi
}


def generate_valid_params_svc(params_svc):
    valid_params = {}

    for kernel_list in params_svc['kernel']:
        kernel = kernel_list[0]  # Estrai il valore del kernel dalla lista
        valid_params[kernel] = []  # Inizializza la lista per ciascun kernel
        
        for C in params_svc['C']:
            
            # Per kernel lineare, ignoriamo gamma e degree
            if kernel == 'linear':
                params = {'kernel': kernel_list, 'C': [C], 'class_weight': ['balanced']}
                valid_params[kernel].append(params)
            
            # Per kernel polinomiale, includiamo degree
            elif kernel == 'poly':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'degree': [2], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
                    
            # Per kernel rbf, includiamo gamma ma ignoriamo degree
            elif kernel == 'rbf':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)
            
            # Per kernel sigmoide, includiamo gamma ma ignoriamo degree
            elif kernel == 'sigmoid':
                for gamma in params_svc['gamma']:
                    params = {'kernel': kernel_list, 'C': [C], 'gamma': [gamma], 'class_weight': ['balanced']}
                    valid_params[kernel].append(params)

    return valid_params



# Generiamo la lista dei parametri validi
valid_params_dict_svc = generate_valid_params_svc(params_svc)

# Crea una lista vuota per contenere tutti i parametri
all_params_svc = []

# Itera su ciascun kernel nel dizionario e aggiungi i parametri alla lista all_params
for kernel_type, params_list in valid_params_dict_svc.items():
    all_params_svc.extend(params_list)
    
    
print(f"\t\t\t\033[1mAll Valid Testable Params will be among these below\033[0m:\n") 
for param_dict in all_params_svc: 
    
    #print(f"\033[1m{param_dict.keys()}\033[0m, {param_dict.values()}")
    
    print("{", end="")  # Inizia il dizionario
    for i, (key, value) in enumerate(param_dict.items()):
        # Formattazione della chiave in grassetto
        bold_key = f"\033[1m{key}\033[0m"
        
        # Se non è l'ultima coppia, aggiungi una virgola
        if i < len(param_dict) - 1:
            print(f"'{bold_key}': {value}, ", end="")
        else:
            print(f"'{bold_key}': {value}", end="")
    
    print("}")  # Chiude il dizionario e va a capo
    

#ATTENZIONE CAMBIA PATH CLASSIFIER!

'''NEW VERSION - EXPERIMENTAL CONDITIONS COUPLED'''

# Base directory aggiornata
base_dir = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_2_classes_1_20Hz'
params_dir = f"{base_dir}/EEG_50_window_25_overlap_coupled_exp_cond/single_patient_optimized_params_coupled_exp_cond_1_20"


for idx_subj, subject_data in new_subject_level_concatenations_coupled_exp_pt_1_20.items():
    
    level_str = 'filtered_1_20'
    
    #if idx_subj == 'pt_17' or idx_subj == 'pt_18' or idx_subj == 'pt_19':
    
    if idx_subj == 'pt_20':
        
        print(f"\n\n\n\t\t\t\t\t\t\033[1mCURRENT SUBJECT {idx_subj}\033[0m\n\n")

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        #for condition in new_subject_level_concatenations_coupled_exp_th_1_20[idx_subj].keys():

        # Itera su ciascuna condizione (ad esempio 'baseline_vs_th_resp', 'baseline_vs_pt_resp', ...)
        for condition, condition_data in subject_data.items():

            #print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Creazione stringa per salvataggio files ('filtered_1_20')
            #level_str == 'filtered_1_20'

            print(f"\nProcessing EEG Data from Preprocessing (i.e.,\033[1m{level_str}\033[0m) for Subject \033[1m{idx_subj}\033[0m")

            # Estraiamo i dati del livello corrente del soggetto corrente della exp cond corrente
            #X = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['data']

            # Estrazione dei dati e delle etichette
            X = condition_data['data']


            # Messaggi di log per dati e label
            print(f"\n\033[1mExtraction of \033[1mData\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            # Estraiamo le del livello corrente del soggetto corrente della exp cond corrente
            #y = new_subject_level_concatenations_coupled_exp_th_1_20[subject][condition]['labels'] 

            y = condition_data['labels']

            print(f"\n\033[1mExtraction of \033[1mLabels\033[0m for Exp Condition \033[1m{condition}\033[0m from Subject \033[1m{idx_subj}\033[0m by the Level \033[1m{level_str}\033[0m")

            '''NEW VERSION'''
            #DIRECTORY PATH PER SALVATAGGIO MODELLI PER FINESTRA DI 50 PUNTI TEMPORALI CON STRIDE DI 25 CAMPIONI
            params_dir = params_dir

            # Creazione della cartella, se non esiste
            if not os.path.exists(params_dir):
                os.makedirs(params_dir)
                print(f"\nCARTELLA CREATA ALLA DIRECTORY: \033[1m{params_dir}\033[0m")


            # Costruzione del percorso del file in maniera dinamica
            params_file_path = f"{params_dir}/optimized_params_{idx_subj}_level_{level_str}_{condition}_std.txt"

            print(f"\n\nPATHFILE PER SOGGETTO \033[1m{idx_subj}\033[0m PER EXP COND \033[1m{condition}\033[0m:\n")

            print(f"\033[1m{params_file_path}\033[0m\n")

            print(f"\n\033[1mShape of data\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {X.shape}")

            y = y.astype(int) 

            print(f"\n\033[1mShape of labels\033[0m for \033[1m{idx_subj}\033[0m from \033[1m{condition}\033[0m: {y.shape}")


            # Calcola il numero totale di etichette livello 4/5°
            label_counts = np.unique(y, return_counts = True)[1]
            total_labels = len(y)

            # Calcola la percentuale di ciascuna classe
            class_proportions = label_counts / total_labels * 100

            print(f"\n\033[1mClass Proportions\033[0m: {class_proportions}")

            # Calcola i pesi delle classi come l'inverso delle proporzioni
            class_weights = torch.tensor([100 / proportion for proportion in class_proportions])

            # Normalizza i pesi in modo che la somma sia uguale al numero delle classi
            class_weights /= class_weights.sum()

            print(f"\n\033[1mClass Weights {class_weights}\033[0m")

            # Crea un dizionario per class_weight
            class_weight_dict = {i: weight for i, weight in enumerate(class_weights)}

            #INIZIALIZZAZIONE SVC

            base_svc = SVC()

            # Memorizza il tempo di inizio
            start_time = time.time()

            # Lista per memorizzare i tempi di esecuzione per ogni finestra temporale
            execution_times = []

            # Contatori per combinazioni valide e non valide
            valid_combination_count = 0
            invalid_combination_count = 0

            # File di output per i parametri ottimizzati
            with open(params_file_path, 'w') as f:
                f.write(f"50 Time Points Window with 25 Stride\tOptimized Parameters\n\n")

            # File di output per i parametri ottimizzati NON validi
            #with open(invalid_params_file_path, 'w') as invalid_f:
            #    invalid_f.write(f"Invalid Parameter Combinations\n\n")


            #INIZIALIZZAZIONE RANDOM SEARCH

            # Lista per memorizzare i risultati delle finestre
            window_results = []

            # Creazione della finestra scorrevole con step e dimensioni desiderate
            n_samples = X.shape[2]
            window_size = 50
            step_size = 25
            n_windows = (n_samples - window_size) // step_size + 1


            #50 TIME-POINTS WITH 25 SLIDING WINDOW APPROACH 

            # Loop attraverso finestre di 50 campioni con stride scorrevole di 25 punti temporali rispetto a quella precedente

            for window_start in range(0, n_samples - window_size + 1, step_size):

                # Memorizza il tempo di inizio per il punto temporale corrente
                time_point_start = time.time()

                # Definiamo la finestra corrente
                window_end = window_start + window_size

                print(f"\n\n\t\t\t\tStarting Random Search for Window \033[1m{window_start}-{window_end}\n\n")

                X_window = X[:, :, window_start:window_end]
                print(f"\n\033[1mX_window[0].shape\033[0m:{X_window[0].shape}")

                # Reshape per adattarsi alla dimensione richiesta da SlidingEstimator
                X_window_reshaped = X_window.reshape(X_window.shape[0], -1)
                print(f"\n\033[1mX_window_reshaped.shape\033[0m:{X_window_reshaped.shape}")

                # Standardizza i dati della finestra corrente
                scaler = StandardScaler()
                X_window_standardized = scaler.fit_transform(X_window_reshaped)
                print(f"\n\033[1mX_window_standardized.shape\033[0m:{X_window_standardized.shape}\n")

                try:
                    print(f"\t\t\t\t\t\033[1mStarting Random Search\033[0m...\n\n")


                    rand_search = RandomizedSearchCV(
                        estimator = base_svc,
                        param_distributions = all_params_svc,
                        scoring ='accuracy',
                        n_iter = 100,
                        verbose = 1,
                        n_jobs = -1
                    )


                    #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    # Esegui RandomizedSearchCV sulla finestra corrente
                    rand_search.fit(X_window_standardized, y)


                    # Controlla il numero totale di combinazioni testate
                    total_combinations_tested = len(rand_search.cv_results_['params'])
                    #print(f"\033[1mTotal combinations tested: {total_combinations_tested}\033[0m")

                    # Salva tutte le combinazioni testate per la finestra corrente
                    with open(params_file_path, 'a') as f:


                        #Estraggo il punteggio medio di test per una specifica combinazione di iper-parametri,
                        #calcolato sulla base di una cross-validation a 5 fold. 
                        #Questo punteggio rappresenta l'accuratezza media del modello su tutti i fold, 
                        #fornendo una sintesi delle sue prestazioni nel test set per ogni soggetto.

                        #In sintesi, è il valore medio di accuracy ottenuto 
                        #mediando il valore di score sul test set, preso dai 5 fold durante la cross-validation,

                        #per una specifica combinazione di iper-parametri!


                        for i, params in enumerate(rand_search.cv_results_['params']):
                            score = rand_search.cv_results_['mean_test_score'][i]
                            f.write(f"\nWindow {window_start}-{window_end}\tTested Params: {json.dumps(params)}, Score: {json.dumps(score)}\n\n")

                        for params in rand_search.cv_results_['params']:
                            if params:
                                valid_combination_count += 1
                            else:
                                #invalid_combination_count += 1
                                print(f"Invalid combination found: {params}")

                        #QUI

                        # Ottieni il modello con i migliori iper-parametri
                        best_model_params = rand_search.best_params_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH
                        best_score = rand_search.best_score_


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                        # Memorizza i risultati della finestra corrente
                        window_results.append({
                            'window_start': window_start,
                            'window_end': window_end,
                            'best_params': best_model_params,
                            'best_score': best_score
                        })


                        #50 TIME-POINT WITH 25 SLIDING WINDOW APPROACH 

                    #Salva i parametri migliori per la finestra corrente in una riga del file di testo
                    with open(params_file_path, 'a') as f:
                        f.write('\n')
                        f.write(f"Best Model Params for Window {window_start}-{window_end}:\t{json.dumps(best_model_params)}, \nBest Score for Window {window_start}-{window_end}:\t{json.dumps(best_score)}\n")
                        f.write('\n')

                except Exception as e:

                    print(f'Error: {e}')

                    # Scrivi la combinazione non valida nel file di output
                    #with open(invalid_params_file_path, 'a') as invalid_f:
                    #    invalid_f.write(f"Invalid Model Params for Window {window_start}-{window_end}:\tInvalid params:{json.dumps(params)}\n")
                    #continue


                    # Memorizza il tempo di fine per il punto temporale corrente
                    time_point_end = time.time()

                    # Calcola il tempo di esecuzione per il punto temporale corrente
                    time_point_elapsed = time_point_end - time_point_start

                    # Aggiungi il tempo di esecuzione alla lista
                    execution_times.append(time_point_elapsed)

                    # Stampa i risultati per il punto temporale corrente
                    #print(f"\nBest model for \033[1mwindow starting at {window_start}\033[0m:")
                    #print(f"\nBest model for \033[1mwindow {window_start}-{window_end}\033[0m:")
                    #print(f"Best Params = {best_model_params}, \nBest Score = {best_score}\n")
                    #print()
                    #print(f"Execution time for \033[1mwindow {window_start}-{window_end}\033[0m: {time_point_elapsed} seconds\n")
                    #print()

            # Analisi finale per identificare la finestra con la massima discriminabilità tra le condizioni sperimentali

            # Definisci il range generale delle finestre che vuoi analizzare
            general_range = [0, 300]  # Puoi modificare il range se necessario

            # Filtra i risultati delle finestre nel range desiderato
            general_results = [res for res in window_results if general_range[0] <= res['window_start'] <= general_range[1]]

            # Controlla se ci sono risultati validi all'interno del range specificato
            if general_results:

                # Trova la finestra con il punteggio migliore
                best_general_window = max(general_results, key=lambda x: x['best_score'])

                # Trova i parametri migliori per questa finestra specifica (se disponibili)
                best_params = next((res['best_params'] for res in window_results if res['window_start'] == best_general_window['window_start'] and res['window_end'] == best_general_window['window_end']), None)
                best_general_window['best_params'] = best_params

                # Stampa le informazioni sulla finestra migliore trovata
                #print(f"\033[1mBest Window Overall\033[0m is in range: \033[1m{best_general_window['window_start']}-{best_general_window['window_end']}\033[0m")
                #print(f"\033[1mBest Params\033[0m: \033[1m{best_general_window['best_params']}\033[0m")
                #print(f"\033[1mBest Score\033[0m: \033[1m{best_general_window['best_score']}\033[0m")

            else:
                print("No valid windows found in the specified range.")


            # Aggiungi il risultato della migliore finestra generale alla lista `window_results`
            window_results.append({
                'Best window_start': best_general_window['window_start'] if general_results else None,
                'Best window_end': best_general_window['window_end'] if general_results else None,
                'best_params': best_general_window['best_params'] if general_results else None,  # Aggiungi i migliori iper-parametri
                'best_score': best_general_window['best_score'] if general_results else None
            })

            # Calcola il tempo di esecuzione totale
            end_time = time.time()
            total_execution_time = end_time - start_time

            #print(f"\033[1mTotal execution time\033[0m: {total_execution_time} seconds")
            #print()
            #print(f"Number of \033[1mvalid combinations\033[0m: {valid_combination_count}")
            #print(f"Number of \033[1minvalid combinations\033[0m: {invalid_combination_count}")

            # Aggiungi il risultato della migliore finestra generale al file di testo
            with open(params_file_path, 'a') as f:
                f.write('\n')
                if general_results:
                    best_general_window = max(general_results, key=lambda x: x['best_score'])
                    f.write(f"BEST WINDOW OVERALL: "),
                    f.write(f"\n\nBest Window Start: {best_general_window['window_start']}"),
                    f.write(f"\nBest Window End: {best_general_window['window_end']}"),
                    f.write(f"\nBest Score: {best_general_window['best_score']}")

                    if best_general_window['best_params'] is not None:
                            f.write(f"\nBest Model Params for Best Window Overall {best_general_window['window_start']}-{best_general_window['window_end']}: {json.dumps(best_general_window['best_params'])}\n")
                    else:
                        f.write("No valid windows found in the specified range.\n")

                    f.write('\n')
                    f.write(f"Total execution time: {total_execution_time} seconds\n")
                    f.write(f"Number of valid combinations: {valid_combination_count}\n")
                    f.write(f"Number of invalid combinations: {invalid_combination_count}\n\n")


#### **ALL SINGLE Patients (PT01-PT20)**

#### Plots of **EACH SINGLE Subject's Accuracy Score Performances** 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI - OLD VERSION**

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX & LEVEL 5 DA COEFF DETAIL DELLE RICOSTRUZIONI**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_pt = {}
    best_scores_level_5_single_pt = {}
    best_scores_level_5_detail_pt = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_pt_level_4_std" o "all_pt_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_pt_level_4_std" o "all_pt_level_5_std"
            if "all_pt_level_4_std" in file_name or "all_pt_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'pt_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            #if level == 4 and subject not in best_scores_level_4_single_pt:
            if level == 'approx_4' and subject not in best_scores_level_4_single_pt:    
                best_scores_level_4_single_pt[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_pt:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_pt:
                best_scores_level_5_single_pt[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_pt:
                best_scores_level_5_detail_pt[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_pt[subject][window] = max(best_scores_level_4_single_pt[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_pt[subject][window] = max(best_scores_level_5_single_pt[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_pt[subject][window] = max(best_scores_level_5_detail_pt[subject][window], best_score)

    return best_scores_level_4_single_pt, best_scores_level_5_single_pt, best_scores_level_5_detail_pt  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_pt_svm, best_scores_level_5_single_pt_svm, best_scores_level_5_detail_pt_svm = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_pt_svm keys\033[0m: {best_scores_level_4_single_pt_svm.keys()}")

for pt_key, window_key in best_scores_level_4_single_pt_svm.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_pt_svm keys\033[0m: {best_scores_level_5_single_pt_svm.keys()}")

for pt_key, window_key in best_scores_level_5_single_pt_svm.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_pt_svm keys\033[0m: {best_scores_level_5_detail_pt_svm.keys()}")

for pt_key, window_key in best_scores_level_5_detail_pt_svm.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER EEG 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_pt = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_pt:    
                best_scores_filtered_1_20_single_pt[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_pt[subject][window] = max(best_scores_filtered_1_20_single_pt[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_pt

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_pt_svm = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_pt_svm keys\033[0m: {best_scores_filtered_1_20_single_pt_svm.keys()}")

for pt_key, window_key in best_scores_filtered_1_20_single_pt_svm.items():
    print(f"\n\n\t\t\t\t\033[1mTherapist: {pt_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
#pwd
#cd ..
#cd New_Plots_Sliding_Estimator_MNE

#path corretta --> cd Plots_Sliding_Estimator_MNE
#path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"

#Comandi da eseguire

#!pwd
#cd Plots_Sliding_Estimator_MNE


import pickle

# Salva il dizionario th_data_dict in un file pkl
with open('best_scores_filtered_1_20_single_pt_svm.pkl', 'wb') as file:
    pickle.dump(best_scores_filtered_1_20_single_pt_svm, file)

#print("Dati concantenati dei Singoli Terapisti salvati in 'subject_level_concatenations_th_1_20.pkl'")

##### **ALL SINGLE Patients (PT01-PT20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX DELLE RICOSTRUZIONI - OLD VERSION**

##### **ALL SINGLE Patients (PT01-PT20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX & LEVEL 5 DA COEFF DETAIL DELLE RICOSTRUZIONI**

In [ ]:
pwd

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO PAZIENTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI APPROX 4, APPROX 5 e DETAIL 5

best_scores_level_4_single_pt_svm, 
best_scores_level_5_single_pt_svm,
best_scores_level_5_detail_pt_svm
'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
    # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    pts_baseline_accuracy_highest_class_in_fold_svm = list()
    
    for subject, scores in best_scores_dict.items():
        
        '''Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_pt:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_pt[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            pts_baseline_accuracy_highest_class_in_fold_svm.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        

        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'approx_4':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ+δ range: 0-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta'
            clf_str = 'svm'
            
        elif level == 'approx_5':
            
            ax1.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)',  fontsize = 16)
            
            level_str = 'delta'
            clf_str = 'svm'
                
                
        elif level == 'detail_5':
            
            ax1.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in  Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)',  fontsize = 16)
            
            level_str = 'theta_strict'
            clf_str = 'svm'
            
        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='b', zorder=5, label=f'Best Score SVM for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='b', zorder=5, label=f'Best Score SVM for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
        
    return pts_baseline_accuracy_highest_class_in_fold_svm

# Esempio di utilizzo
save_path_level_4 = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5 = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'
save_path_level_5_detail = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
pts_baseline_accuracy_highest_class_in_fold_level_4_xgb = plot_best_scores_for_subjects(best_scores_level_4_single_pt_svm, 'approx_4', save_path_level_4)
pts_baseline_accuracy_highest_class_in_fold_level_5_xgb = plot_best_scores_for_subjects(best_scores_level_5_single_pt_svm, 'approx_5', save_path_level_5)
pts_baseline_accuracy_highest_class_in_fold_level_5_detail_xgb = plot_best_scores_for_subjects(best_scores_level_5_detail_pt_svm, 'detail_5', save_path_level_5)

In [ ]:
#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#import pickle

# Salvare l'intero dizionario annidato con pickle
#with open('pts_baseline_accuracy_highest_class_in_fold_svm.pkl', 'wb') as f:
#    pickle.dump(pts_baseline_accuracy_highest_class_in_fold_svm, f)

    
# Salvare l'intero dizionario annidato con pickle
import pickle

with open('best_scores_level_4_single_pt_svm.pkl', 'wb') as f:
    pickle.dump(best_scores_level_4_single_pt_svm, f)

with open('best_scores_level_5_single_pt_svm.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_single_pt_svm, f)

with open('best_scores_level_5_detail_pt_svm.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_detail_pt_svm, f)
    
    
#print(f"len(pts_baseline_accuracy_highest_class_in_fold_level_4_xgb): {len(pts_baseline_accuracy_highest_class_in_fold_level_4_xgb)}")    
#print(f"len(pts_baseline_accuracy_highest_class_in_fold_level_5_xgb): {len(pts_baseline_accuracy_highest_class_in_fold_level_5_xgb)}")


    
#import pickle 
# Caricare il dizionario salvato con pickle
#with open('/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations_th.pkl', 'rb') as f:
#   subject_level_concatenations_th = pickle.load(f)

##### **ALL SINGLE Patients (PT01-PT20) CODE PER PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
!pwd

In [ ]:
# Salvare l'intero dizionario annidato con pickle
import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)

In [ ]:
new_subject_level_concatenations_pt_1_20.keys()

In [ ]:
#new_subject_level_concatenations_pt_1_20.keys()
#dict_keys(['pt_1', 'pt_2', 'pt_3', 'pt_4', 'pt_5', 'pt_6', 'pt_7', 'pt_8', 'pt_9', 'pt_10', 'pt_11', 'pt_12', 'pt_13', 'pt_14', 'pt_15', 'pt_16'])

#new_subject_level_concatenations_pt_1_20['pt_16'].keys()
#dict_keys(['data', 'labels'])

In [ ]:
'''
UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE E TEMPO ASSIEME! RESULTS SU SINGOLO SOGGETTO PAZIENTI - NEW VERSION

AGGIUNTA DEI SCORE ASSOCIATI A BEST SCORE DI FILTERED 1-20Hz

best_scores_filtered_1_20_single_pt_svm
'''


import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_best_scores_for_subjects(best_scores_dict, level, save_path):
    
    '''Creazione sottocartella per ogni soggetto'''
    
     # Controlla e crea la directory principale "plots" se non esiste
    plots_dir = os.path.join(save_path, 'plots_1_20')
    os.makedirs(plots_dir, exist_ok=True)
    
    #print(plots_dir)
    
    pts_baseline_accuracy_highest_class_in_fold_svm = list()
    
    for subject, scores in best_scores_dict.items():
        
        ''' Crea la directory per il soggetto'''
        
        #subject_dir = os.path.join(save_path, f'single_{subject}')
        
        subject_dir = os.path.join(plots_dir, f'single_{subject}_filtered_1_20')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        #Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #windows: ['0-50', '25-75', '50-100', '75-125', '100-150', '125-175', '150-200', '175-225', '200-250', '225-275', '250-300']

        #Creo una lista delle valori di best score associati alle chiavi di secondo ordine delle finestre considerate
        scores_list = [scores[window]for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        #scores_list: [0.2681818181818182, 0.2681818181818182, 0.2681818181818182, 0.2621212121212121, 
                    #  0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 0.2621212121212121, 
                    #  0.2681818181818182, 0.2621212121212121, 0.2621212121212121]

        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th:
        if subject in new_subject_level_concatenations_pt_1_20:    
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_pt_1_20[subject]['labels']
            
            #print(type(labels))

            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 

            #print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")

            #print(f"type of labels_counts is {type(unique_values)}")
            #print(f"\nTot Labels: {np.sum(labels_counts)}")
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")

            pts_baseline_accuracy_highest_class_in_fold_svm.append(baseline_accuracy_highest_class_in_fold)
            
        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        windows = list(scores.keys())
        scores_list = [scores[window] for window in windows]

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]
        
        '''MODIFICHE NUOVE'''
        plt.figure(figsize=(30, 12))
        ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''MODIFICHE NUOVE'''
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        prestimulus_added_ax1 = False
        prestimulus_added_ax2 = False

        '''MODIFICHE NUOVE'''

        # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
        if level == 'filtered_1_20':
            
            ax1.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
            ax2.set_title(f'Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG Preprocessed (IIR-filter 1-20 Hz)',  fontsize = 16)
            
            level_str = 'filtered_1_20'
            clf_str = 'svm'
            

        '''PLOTS NEL DOMINIO DELLE FINESTRE'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax1:
            ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
            prestimulus_added_ax1 = True

        ax1.plot(window_mid_points_in_ms, scores_list, color='b', zorder=5, label=f'Best Score SVM for {subject} in $i^{{th}}$ window')

        #ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio finestre (ax1)
        ax1.set_xticks(tick_positions)
        ax1.set_xticklabels(window_labels)

        # Modifica del fontsize dei tick dell'asse x ed y
        ax1.tick_params(axis='x', labelsize=18)
        ax1.tick_params(axis='y', labelsize=18)

        ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
        ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
        ax1.grid(True)

        '''PLOTS NEL DOMINIO DEL TEMPO'''

        # Aggiungi la linea di prestimolo solo la prima volta
        if not prestimulus_added_ax2:
            ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
            prestimulus_added_ax2 = True


        ax2.plot(window_mid_points_in_ms, scores_list, color='b', zorder=5, label=f'Best Score SVM for {subject} in $i^{{th}}$ window')

        #ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

        ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subject {subject}')

        # Imposta le etichette principali per il dominio temporale (ax2)
        ax2.set_xticks(window_mid_points_in_ms)
        ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

        # Modifica del fontsize dei tick dell'asse x ed y
        ax2.tick_params(axis='x', labelsize=18)
        ax2.tick_params(axis='y', labelsize=18)

        ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
        ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

        ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
        ax2.grid(True)

        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'best_scores_subject_{subject}_{level_str}_{clf_str}.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')
        
    return pts_baseline_accuracy_highest_class_in_fold_svm

# Esempio di utilizzo
save_path_filtered_1_20 = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

# Esegui la funzione per ogni livello'
pts_baseline_accuracy_highest_class_in_fold_1_20_svm = plot_best_scores_for_subjects(best_scores_filtered_1_20_single_pt_svm, 'filtered_1_20', save_path_filtered_1_20)

#### **All Patients (PT01-PT20)**

#### Plots of **Grand Average Mean** of Best Single Subject's Accuracy Score Performances 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **NEW VERSION**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
!pwd

In [ ]:
'''NEW VERSION'''


import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_level_4_single_pt = {}
    best_scores_level_5_single_pt = {}
    best_scores_level_5_detail_pt = {}  # Nuovo dizionario per i coefficienti di dettaglio

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_pt_level_4_std" o "all_pt_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_pt_level_4_std" o "all_pt_level_5_std"
            if "all_pt_level_4_std" in file_name or "all_pt_level_5_std" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "_level_approx_4_std" in file_name:
                #level = 4
                level = 'approx_4'
            elif "_level_approx_5_std" in file_name:
                #level = 5
                level = 'approx_5'
            elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                level = "detail_5"
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            #if level == 4 and subject not in best_scores_level_4_single_pt:
            
            if level == 'approx_4' and subject not in best_scores_level_4_single_pt:    
                best_scores_level_4_single_pt[subject] = {w: float('-inf') for w in n_windows}
            #elif level == 5 and subject not in best_scores_level_5_single_pt:
            elif level == 'approx_5' and subject not in best_scores_level_5_single_pt:
                best_scores_level_5_single_pt[subject] = {w: float('-inf') for w in n_windows}
            elif level == "detail_5" and subject not in best_scores_level_5_detail_pt:
                best_scores_level_5_detail_pt[subject] = {w: float('-inf') for w in n_windows}  # Inizializza il nuovo dizionario
            
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            #if level == 4:
                            if level == 'approx_4':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_level_4_single_pt[subject][window] = max(best_scores_level_4_single_pt[subject][window], best_score)
                            #elif level == 5:
                            elif level =='approx_5':
                                best_scores_level_5_single_pt[subject][window] = max(best_scores_level_5_single_pt[subject][window], best_score)
                            elif level == "detail_5":  # Nuova logica per i coefficienti di dettaglio
                                best_scores_level_5_detail_pt[subject][window] = max(best_scores_level_5_detail_pt[subject][window], best_score)

    return best_scores_level_4_single_pt, best_scores_level_5_single_pt, best_scores_level_5_detail_pt  # Ritorna anche il nuovo dizionario

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params"  # Fornisci il tuo percorso
best_scores_level_4_single_pt_svm, best_scores_level_5_single_pt_svm, best_scores_level_5_detail_pt_svm = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Level 4 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_pt_svm keys\033[0m: {best_scores_level_4_single_pt_svm.keys()}")

for th_key, window_key in best_scores_level_4_single_pt_svm.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_pt_svm keys\033[0m: {best_scores_level_5_single_pt_svm.keys()}")

for th_key, window_key in best_scores_level_5_single_pt_svm.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

# Stampa i risultati per i best scores dei coefficienti di dettaglio
print(f"\n\n\t\t\t\t\t\t\t\t\033[1mBest Scores Level 5 Detail Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_detail_pt_svm keys\033[0m: {best_scores_level_5_detail_pt_svm.keys()}")

for th_key, window_key in best_scores_level_5_detail_pt_svm.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()


In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        '''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")

        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_4 = calculate_mean_and_confidence_interval(best_scores_level_4_single_pt_svm, n_windows)
statistics_level_5 = calculate_mean_and_confidence_interval(best_scores_level_5_single_pt_svm, n_windows)
statistics_level_5_detail = calculate_mean_and_confidence_interval(best_scores_level_5_detail_pt_svm, n_windows)

In [ ]:
'''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
#print(best_scores_level_4_single_pt_svm['th_1']['0-50'])
#print(best_scores_level_4_single_pt_svm['th_2']['0-50'])
#print(best_scores_level_4_single_pt_svm['th_3']['0-50'])
#print()
#print(best_scores_level_4_single_pt_svm['th_1']['25-75'])
#print(best_scores_level_4_single_pt_svm['th_2']['25-75'])
#print(best_scores_level_4_single_pt_svm['th_3']['25-75'])


In [ ]:
type(statistics_level_4)

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
!pwd

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open('new_all_pt_concat_reconstructions.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_pt['pt_1'].keys()

In [ ]:
new_all_pt_concat_reconstructions.keys()

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME '''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    subjects_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    os.makedirs(subjects_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 4:
        level_str = 'theta'
    elif level == 5:
        level_str = 'delta'
    elif level == '5_detail':
        level_str = 'theta_strict'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'all_ths_level_{level_str}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    print(f"\n\t\t\t\t\t\033[1mPatients'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_pt_concat_reconstructions.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            #print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            #print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            #print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            #print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            #print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            #print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            #print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    
    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)

    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Aggiunge il livello di baseline in base al livello specificato
    #if level == 4:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range')
    #elif level == 5:
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range')
    #elif level == '5_detail':
    #    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    #    plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Detail Range')
    
    '''VECCHIO'''
    
    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
    # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
    if level_str == 'theta':
        ax1.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range', fontsize = 16)
        ax2.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ+δ Range',  fontsize = 16)
        
    elif level_str == 'delta':
        ax1.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)
        ax2.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - δ Range',  fontsize = 16)

    elif level_str == 'theta_strict':
        ax1.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
        ax2.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level} - Θ Range',  fontsize = 16)
    
    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_pts_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(subjects_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'Plot salvato in: \n\033[1m{save_file_path}\033[1m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_4, 4, save_path)
plot_mean_best_scores_for_window(statistics_level_5, 5, save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail, '5_detail', save_path)

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE E PLOTS BEST PERFORMANCES SALVATE PER EEG PREPROCESSED FILTERED 1-20Hz**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    

 # Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_all_pt_concat_reconstructions_1_20.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions_1_20 = pickle.load(f)

In [ ]:
print(new_subject_level_concatenations_pt_1_20.keys())
print()
print(new_subject_level_concatenations_pt_1_20['pt_1'].keys())
print(new_subject_level_concatenations_pt_1_20['pt_1']['data'].shape)
print()
print(new_all_pt_concat_reconstructions_1_20.keys())
print(new_all_pt_concat_reconstructions_1_20['data'].shape)

In [ ]:
# VERSIONE SENZA CALCOLO MEDIA E DEVIAZIONE STANDARD  

'''NEW VERSION'''

import os
import re

# Funzione per leggere i file txt e estrarre i best score separati per soggetto
def extract_best_scores_by_subject(folder_path):
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    best_scores_filtered_1_20_single_pt = {}

    # Itera sui file nella directory
    for file_name in os.listdir(folder_path):
        file_path = os.path.join(folder_path, file_name)
        
        # Controlla se il file è un .txt e contiene "all_th_level_4_std" o "all_th_level_5_std"
        if file_name.endswith(".txt"):
            
            # Escludi i file che contengono "all_th_level_4_std" o "all_th_level_5_std"
            if "invalid_params" in file_name:
                continue  # Salta il file
            
            # Determina il livello dal nome del file
            if "filtered_1_20_std" in file_name:
                level = 'filtered_1_20'
            else:
                continue  # Salta il file se non è né livello 4 né livello 5
            
            # Estrai il soggetto dal nome del file (ad es. 'th_1')
            subject_match = re.search(r'pt_\d+', file_name)
            if subject_match:
                subject = subject_match.group(0)
            else:
                continue  # Salta il file se non riesce a trovare il soggetto
            
            # Inizializza i dizionari per il soggetto se non esistono
            
            
            if level == 'filtered_1_20' and subject not in best_scores_filtered_1_20_single_pt:    
                best_scores_filtered_1_20_single_pt[subject] = {w: float('-inf') for w in n_windows}
           
            # Leggi il file
            with open(file_path, 'r') as file:
                lines = file.readlines()
            
            # Cerca le righe con "Best Score for Window"
            for line in lines:
                for window in n_windows:
                    pattern = f"Best Score for Window {window}:"
                    if pattern in line:
                        # Estrai il valore float dalla riga
                        match = re.search(rf"{pattern}\s+([0-9]*\.?[0-9]+)", line)
                        if match:
                            best_score = float(match.group(1))
                            if level == 'filtered_1_20':
                                # Aggiorna solo se il nuovo punteggio è maggiore
                                best_scores_filtered_1_20_single_pt[subject][window] = max(best_scores_filtered_1_20_single_pt[subject][window], best_score)
                
    return best_scores_filtered_1_20_single_pt

# Esegui la funzione su una cartella specifica
folder_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20"  # Fornisci il tuo percorso
best_scores_filtered_1_20_single_pt_svm = extract_best_scores_by_subject(folder_path)

# Stampa o salva i risultati
print(f"\t\t\t\t\t\t\t\t\033[1mBest Scores Filtered 1_20 Hz Structure\033[0m:\n")
print(f"\033[1mbest_scores_filtered_1_20_single_pt_svm keys\033[0m: {best_scores_filtered_1_20_single_pt_svm.keys()}")

for th_key, window_key in best_scores_filtered_1_20_single_pt_svm.items():
    print(f"\n\n\t\t\t\t\033[1mPatient: {th_key}\033[0m\n")
    for window, window_value in window_key.items():
        print(f"\033[1m{window}\033[0m: {window_value}")
    print()

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA - NEW VERSION'''

import numpy as np
import scipy.stats as stats


n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, windows, confidence_level = 0.95):
    
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti
        scores = [subject_scores[window] for subject_scores in best_scores.values()]
        
        '''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")

        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per i best scores di livello 4 e salva in dizionario
statistics_level_1_20 = calculate_mean_and_confidence_interval(best_scores_filtered_1_20_single_pt_svm, n_windows)

In [ ]:
'''CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW''' 
#print(best_scores_filtered_1_20_single_pt_svm['th_1']['0-50'])
#print(best_scores_filtered_1_20_single_pt_svm['th_2']['0-50'])
#print(best_scores_filtered_1_20_single_pt_svm['th_3']['0-50'])
#print()
#print(best_scores_filtered_1_20_single_pt_svm['th_1']['25-75'])
#print(best_scores_filtered_1_20_single_pt_svm['th_2']['25-75'])
#print(best_scores_filtered_1_20_single_pt_svm['th_3']['25-75'])

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DELLE FINESTRE e TEMPO ASSIEME'''



import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_dict, level, save_path):
    
    # Crea la directory per il soggetto
    
    data_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    os.makedirs(data_dir, exist_ok=True)
    
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Imposta il livello e la directory di salvataggio
    if level == 'filtered_1_20':
        level_str = 'filtered_1_20'
    else:
        raise ValueError("Livello non riconosciuto")

    # Crea la directory per il livello specifico
    #subjects_dir = os.path.join(save_path, f'plot_mean_all_pts_level_{level}')
    #os.makedirs(subjects_dir, exist_ok=True)
    
    # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
    #print(f"\n\t\t\t\t\t\033[1mPatients'scores for level: {level}\033[0m\n")
    
    for key, value in new_all_pt_concat_reconstructions_1_20.items():
        
        if "labels" in key:
            
            #Prendo il vettore delle labels di quel soggetto specifico
            labels = value

            #print(type(labels))
            
            unique_values, labels_counts = np.unique(labels, return_counts = True)

            #Definisco il n° fold applicate per i dati di ogni soggetto 
            num_folds = 5 
            
            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1mAll Subjects\033[0m: {np.sum(labels_counts)}")

            #Calcolo il numero di elementi di ogni fold 
            elements_per_fold = total_labels/5

            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\nElements per Fold for \033[1mAll Subjects\033[0m: {rounded_elements_per_fold}")
            
            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            print(f"\nClass Percentage for \033[1mAll Subjects\033[0m: {class_percentage}")

            #Estraggo la percentuale della classe più grande 
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1mAll Subjects\033[0m is: {highest_class_percentage}")

            #Calcolo il n° campioni della classe più grande nel singolo fold arrotondando "per eccesso"
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage/100)

            print(f"\n\033[1mN° Samples for Highest Class for \033[1mAll Subjects\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1mAll Subjects\033[0m is: {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class/rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1mAll Subjects\033[0m is: {baseline_accuracy_highest_class_in_fold}\n\n\n")
            
    for window in n_windows:
        
        # Liste di intervalli per ogni finestra
        windows = list(statistics_dict.keys())
        mean_scores_list = [statistics_dict[window]['mean'] for window in windows]
        ci_lower_list = [statistics_dict[window]['ci_lower'] for window in windows]
        ci_upper_list = [statistics_dict[window]['ci_upper'] for window in windows]
        
        
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
        window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    '''VECCHIO'''
    # Inizio del plot
    #plt.figure(figsize=(10, 7))
    
    '''MODIFICHE NUOVE'''
    plt.figure(figsize=(30, 12))
    ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
    ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale

    
    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''MODIFICHE NUOVE'''
    # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
    prestimulus_added_ax1 = False
    prestimulus_added_ax2 = False
    
    '''VECCHIO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)
    
    '''VECCHIO'''
    # Aggiunge i punti medi delle finestre
    #plt.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    '''VECCHIO'''
    # Aggiunge l'intervallo di confidenza
    #plt.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

    '''VECCHIO'''
    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
    
    '''VECCHIO'''
    # Linea orizzontale per il chance level
    #plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    #plt.title(f'Logistic Regression - Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)')

    #plt.xlabel('Windows (50 samples)', fontweight='bold')
    #plt.ylabel('Mean Best Accuracy Score', fontweight='bold')
    #plt.legend(loc='best')
    #plt.grid(True)
    
    '''MODIFICHE NUOVE'''
    
     # Se il livello è filtered_1_20, gestisci i titoli per i grafici su ax1 e ax2
    if level == 'filtered_1_20':

        ax1.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)
        ax2.set_title(f'SVM - Mean Best Accuracy Score in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed (IIR-filter 1-20 Hz)', fontsize = 16)

    '''PLOTS NEL DOMINIO DELLE FINESTRE'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax1:
        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        prestimulus_added_ax1 = True

    ax1.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax1.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')
    
    ax1.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio finestre (ax1)
    ax1.set_xticks(tick_positions)
    ax1.set_xticklabels(window_labels)

    # Modifica del fontsize dei tick dell'asse x ed y
    ax1.tick_params(axis='x', labelsize=18)
    ax1.tick_params(axis='y', labelsize=18)

    ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
    ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
    ax1.grid(True)
                 
    '''PLOTS NEL DOMINIO DEL TEMPO'''
                
    # Aggiungi la linea di prestimolo solo la prima volta
    if not prestimulus_added_ax2:
        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        prestimulus_added_ax2 = True


    ax2.plot(window_mid_points_in_ms, mean_scores_list, color='b', zorder=5, label=f'Mean Best Score for Each Tested Window')
    
    ax2.fill_between(window_mid_points_in_ms, ci_lower_list, ci_upper_list, color='b', alpha=0.2, label='Confidence Interval')

    ax2.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label='Chance Level')
    
    # Imposta le etichette principali per il dominio temporale (ax2)
    ax2.set_xticks(window_mid_points_in_ms)
    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])

    # Modifica del fontsize dei tick dell'asse x ed y
    ax2.tick_params(axis='x', labelsize=18)
    ax2.tick_params(axis='y', labelsize=18)

    ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
    ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)

    ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
    ax2.grid(True)

    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_pts_level_{level_str}_window_and_time_domain.png'
    save_file_path = os.path.join(data_dir, filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'\nPlot salvato in: \n\033[1m{save_file_path}\033[0m\n')

# Esempio di utilizzo
save_path = f'/home/stefano/Interrogait/{familiar_path}/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_1_20, 'filtered_1_20', save_path)

## **All Classifiers: Logistic Regression, XGBoost, SVM**

#### **ALL SINGLE Therapists (TH01-TH20)**

#### Plots of **EACH SINGLE Subject's Accuracy Score Performances** 

- ##### Obtained for **EACH window** for all the **3 CLASSIFIERS**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

#### **Istruzioni del codice qui sotto**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

##### **Descrizione degli step nel codice per estrarre dalle relative paths dei vari modelli (i.e., LOGISTIC REGRESSION, XGBOOST, SVM) le best score performances salvate per il level 4 e 5 dalle ricostruzioni**:

Fammi un codice python che faccia queste cose 

- **1)** Entrami in una **folder path** (che ti fornisco io) ed iteri in quella folder path

che sarà questa

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/"

qui troverai 3 cartelle, una che si chiama 'logistic_regression' una 'xgboost' ed una 'svm', 
dentro ognuna troverai questo sotto-path (uguale per tutte)

"/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/" al cui interno poi troverai
due cartelle (uguali per tutte e tre):

single_therapists_optimized_params
single_patients_optimized_params

voglio che entri, per ognuna delle 3 cartelle (i.e. una che si chiama 'logistic_regression' una 'xgboost' ed una 'svm’), quindi a questo livello di path

/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression
/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/xgboost
/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/svm

dentro la relativa sotto cartella "single_therapists_optimized_params" quindi dovrai entrare dentro ciascuna sotto-path che ti metto qui sotto

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

- **2)** Vedi se dentro ognuna di queste 3 sotto-path sopra, dentro la cartella "single_therapists_optimized_params" ci siano **file che finiscono con .txt**: 

- **3)** Per ogni file, vedi se contiene la stringa 
**"invalid_params"** 

e se incontri questa stringa, **escludi quei file .txt** e continua.. 

- **4)** Vedi invece se il file contiene la stringa **"optimized_params"** e **"_level_4_std"** o **"optimized_params"** **"_level_5_std**:

- - **4.1.)** In quel caso, entri dentro quel file e **leggilo** ma poi fai una ulteriore considerazione, ossia 
- - vedi se quello che precede "_level_4_std" o "_level_5_std" sia **" th_"** dove * è un **suffisso dinamico**, che va da
1 a 15...

Quindi avrai per ogni soggetto, due file .txt, che finiranno con questa stringa 

Per il **soggetto 1**: "**th_1_level_4_std**" o "**th_1_level_5_std**" 
Per il **soggetto 2**: "**th_2_level_4_std**" o "**th_2_level_5_std**" 

E così via, fino al 15° soggetto...

Di conseguenza, per ogni sotto-path che ti metto qui sotto

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

dovrai entrare dentro le coppie di file .txt relative allo stesso soggetto, per i due livelli di ricostruzione del segnale. 

Di conseguenza entrerai in totale, per il soggetto 'th_1' ad esempio dentro i suoi 6 relativi file, che trovi a coppie dentro le relative sotto-path che ti ho detto sopra , che son

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

- **5)** A quel punto, vedi in ognuna delle coppie di file .txt dentro la relativa sotto-path dello stesso soggetto

(i.e., ossia per esempio avrai per il soggetto 1 due file .txt, che finiranno con questa stringa 

"th_1_level_4_std" o "th_1_level_5_std" )

- **7)** Leggi il file .txt e vedi se ci sia un **riga in quel file .txt** con scritto 

**"Best Score for Window"**, seguito da **una sequenza di stringhe dinamica**, che cambia e che può essere presa da una lista di stringhe iterativamente che si costruisce a priori, del tipo:

"0-50" "25-75" etc., ossia che cambia di 25 valori ogni volta in maniera uniforme, quindi proseguendo sarebbe:
"50-100" "75-125" "100-150" "125-175" "150-200" "175-225" "200-250" "225-275" "250-300"

Quindi la lista di stringa dinamica potrebbe essere

**n_windows** = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"]

di conseguenza, itera per ogni elemento di questa lista "n_windows" per riconoscere se questa **sequenza di stringa dinamica** completi un riga dentro il file .txt che avrà scritto quindi:

**"Best Score for Window" + {elemento della lista "n_windows}**:"

A questo punto, avrai l'intera riga che sarà ad esempio:

"Best Score for Window 0-50: ".. 

In quella stessa riga del file .txt, dovresti trovare un **valore float**.. 

- **8)** Vorrei che prendessi quel valore float e **lo appendessi ad un dizionario**, che conterrà nei suoi vari valori i vari **best score ottenuti da quel soggetto lì, per lo specifico classificatore per ciascuna delle finestra considerate** , 
(che vanno da 0-50 a 250-300, ossia prendendo a riferimento quello che c'è dentro "n_windows"

'n_windows = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"])

Questo dizionario lo chiamerò ad esempio **"best_scores_level_4_single_th"**, che ad esempio avrà, 

come primo "valore", la chiave di altro dizionario, associata alla stringa che si riferisce al soggetto iterato (th_1, th_2 etc) 

e come valore ci sarà un altro dizionario, 

che avrà come chiave il nome della stringa che si riferisce al classificatore testato per quel soggetto lì, 
e che si riferisce al folder del relativo classificatore, (i.e., una volta sarà **logistic_regression**, una volta sarà **xgboost** e una volta sarà **svm**) 

dentro poi ogni sotto-sotto-chiave, ci sarà poi un altro dizionario ancora, che avrà 

- - **A)** come sotto-sotto-sotto-chiave il nome dell'elemento iterato rispetto a "n_windows" e 
- - **B)** come sotto-sotto-sotto-valore il valore float associato al best score trovato per quella finestra lì, per quel soggetto lì, per quel classificatore lì, del tipo

per il sottodizioario **logistic_regression** in riferimento al soggetto ad esempio "th_1":

{*logistic_regression*}: { {'**0-50**': valore float del best score ottenuto dal soggetto 1 sulla finestra 0-50, }
{’25-75’: valore float del best score ottenuto dal soggetto 1 sulla finestra 25-75... etc] }

per **xgboost** in riferimento al soggetto ad esempio "th_1":

{*xgboost*} = {{‘**0-50**': valore float del best score ottenuto dal soggetto 1 sulla finestra 0-50, }
{{’25-75’}: valore float del best score ottenuto dal soggetto 1 sulla finestra 25-75... etc] }

per **svm** in riferimento al soggetto ad esempio "th_1":

{*svm*} = {{‘**0-50**': valore float del best score ottenuto dal soggetto 1 sulla finestra 0-50, }
{’25-75’}: valore float del best score ottenuto dal soggetto 1 sulla finestra 25-75... etc] 

quindi in sostanza, "**best_scores_level_4_single_th**" sarà un **dizionario annidato**, 

che conterrà come primo dizionario come chiave il nome del soggetto iterato (th_1, th_2 etc) che avrà come valore, 

altri 3 dizionari (quelli dei 3 classificatori rispetto al soggetto th_1) , ognuno che ha come chiave il nome del classificatore 

(quindi *logistic regression* *xgboost* e *svm*)

e poi

come sotto-sotto-sotto- valore di ogni sotto-sotto-dizionario del relativo classificatore, 


un altro dizionario, che ha come chiave il valore stringa di quella finestra, e 
come sotto-sotto-sotto-sotto-valore, 

il valore di best score ottenuto da quel soggetto lì, per quella finestra testata, per quel classificatore lì, ognuno dopo l'altro ...

Infatti, percorrendo tutto il file .txt, avrai altre righe in cui potrebbe comparire questa sequenza di stringhe del tipo 

"Best Score for Window {elemento di n_windows} ".. 

Quindi, alla fine, creerò un numero di dizionari pari al numero di soggetti, ossia 

th_1
th_2
th_3
th_4
th_5
th_6
th_7
th_8
th_9
th_10
th_11
th_12
th_13
th_14
th_15

dove ciascuno conterrà altri 3 dizionari 

(quelli dei classificatori testati per il relativo soggetto) seguito da

un altro dizionario, che ha come chiavi il numero di finestre per cui ho calcolato il best score per la relativa finestra, che sarà diversa per ogni finestra ovviamente 

e come valore di quest'ultimo dizionario, il valore di best score ottenuto da quel soggetto lì, per quella finestra lì, con quello specifico classificatore...

Quindi, la costruzione di questi dizionari annidati sarà del tipo:

th_1 --> dentro *logistic regression*, *xgboost*, *svm* dentro ognuno avrò questa struttura ad esempio

0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121

Ognuna, quindi, dovrà conteggiare 

i best score ottenuti da ogni singolo soggetto, 
per quello specifico classificatore,
per quella finestra di segnale EEG, 
per il livello di ricostruzione considerato,

(che è identificato dall'aver visto se la porzione finale della stringa associata al nome del file contenga la stringa "_level_4_std" o "_level_5_std, quando iteri dentro la folder path)...


<br>

Infatti, la stessa sequenza di passaggi vorrei che venisse eseguita quando si controlla che la porzione finale della stringa associata al nome del file contenga la stringa "_level_5_std" ...

quindi in quel caso creerò un altro dizionario **best_scores_level_5_single_th**, con dentro una stessa struttura ossia


th_1 (con dentro *logistic regression*, *xgboost*, *svm* )
th_2 (con dentro *logistic regression*, *xgboost*, *svm* )
th_3 (con dentro *logistic regression*, *xgboost*, *svm* )
th_4 (con dentro *logistic regression*, *xgboost*, *svm* )
th_5 (con dentro *logistic regression*, *xgboost*, *svm* )
th_6 (con dentro *logistic regression*, *xgboost*, *svm* )
th_7 (con dentro *logistic regression*, *xgboost*, *svm* )
th_8 (con dentro *logistic regression*, *xgboost*, *svm* )
th_9 (con dentro *logistic regression*, *xgboost*, *svm* )
th_10 (con dentro *logistic regression*, *xgboost*, *svm* )
th_11 (con dentro *logistic regression*, *xgboost*, *svm* )
th_12 (con dentro *logistic regression*, *xgboost*, *svm* )
th_13 (con dentro *logistic regression*, *xgboost*, *svm* )
th_14 (con dentro *logistic regression*, *xgboost*, *svm* )
th_15 (con dentro *logistic regression*, *xgboost*, *svm* )


ognuna con dentro 


0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121




<br>

Quindi che nel codice voglio che si prenda dal relativo file .txt del soggetto 

(per i due livelli di ricostruzione del segnale, ossia ad esempio dentro la sotto-path del folder associato ad ogni classificatore del primo soggetto 
 "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"
 acceda dentro 

"optimized_params_th_1_level_4_std.txt" e 
"optimized_params_th_1_level_5_std.txt"

E, per ogni finestra considerata
(i.e., n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
"150-200", "175-225", "200-250", "225-275", "250-300"])

Mi appenda, nella relativa sottochiave del sotto-dizionario associato al classificatore dello specifico soggetto, il migliore best score che il soggetto ad esempio 1 ha ottenuto quella finestra lì, per quel livello di ricostruzione lì, per quel classificatore lì (accedendo come ti ho detto alle varie sotto-path dei folder dei classificatori)....

ossia per la prima che sarà 0-50
e così via per le altre...

e che la stessa cosa la deve fare per ogni soggetto (th_2, th_3 etc.)


<br>
<br>
<br>




##### **ALL SINGLE Therapists (TH01-TH15) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DALLE RICOSTRUZIONI DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) - OLD VERSION**

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations_th.pkl', 'rb') as f:
    subject_level_concatenations_th = pickle.load(f)

In [ ]:
import os

def process_txt_files(base_path, classifiers, n_windows):
    best_scores_level_4 = {}
    best_scores_level_5 = {}
    
    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(base_path, classifier, "EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params")
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)
                
                # Escludi i file che contengono "invalid_params", "all_th_level_4", o "all_th_level_5"
                if "invalid_params" in file_name or 'all_th_level_4' in file_name or 'all_th_level_5' in file_name:
                    continue
                
                # Verifica se il file è per livello 4 o livello 5
                if "optimized_params" in file_name:
                    
                    # Verifica se il file è per il livello 4
                    if "_level_4_std" in file_name:
                        
                        # Verifica che il file sia per uno specifico soggetto (th_1, th_2, ..., th_15)
                        subject = None
                        if "th_" in file_name:
                            try:
                                subject = file_name.split("th_")[1].split("_")[0]  # Estrai il numero del soggetto (1-15)
                                subject = int(subject)  # Converte in intero per verificare che sia un numero valido
                                subject_key = f"th_{subject}"  # Se tutto va bene, crea la chiave
                            except (IndexError, ValueError):
                                print(f"Errore nel file name: {file_name}")
                                continue  # Se c'è un errore, passa al prossimo file
                            
                            # Crea la struttura del dizionario se non esiste
                            if subject_key not in best_scores_level_4:
                                best_scores_level_4[subject_key] = {}

                            if classifier not in best_scores_level_4[subject_key]:
                                best_scores_level_4[subject_key][classifier] = {}

                            # Leggi il file .txt
                            with open(file_path, 'r') as f:
                                lines = f.readlines()

                                # Cerca la riga che inizia con "Best Score for Window" e il valore float
                                for line in lines:
                                    for window in n_windows:
                                        if f"Best Score for Window {window}:" in line:
                                            try:
                                                score = float(line.split(":")[1].strip())
                                                best_scores_level_4[subject_key][classifier][window] = score
                                            except ValueError:
                                                print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                            break

                    # Verifica se il file è per il livello 5
                    elif "_level_5_std" in file_name:
                        # Verifica che il file sia per uno specifico soggetto (th_1, th_2, ..., th_15)
                        subject = None
                        if "th_" in file_name:
                            try:
                                subject = file_name.split("th_")[1].split("_")[0]  # Estrai il numero del soggetto (1-15)
                                subject = int(subject)  # Converte in intero per verificare che sia un numero valido
                                subject_key = f"th_{subject}"  # Se tutto va bene, crea la chiave
                            except (IndexError, ValueError):
                                print(f"Errore nel file name: {file_name}")
                                continue  # Se c'è un errore, passa al prossimo file
                            
                            # Crea la struttura del dizionario se non esiste
                            if subject_key not in best_scores_level_5:
                                best_scores_level_5[subject_key] = {}

                            if classifier not in best_scores_level_5[subject_key]:
                                best_scores_level_5[subject_key][classifier] = {}

                            # Leggi il file .txt
                            with open(file_path, 'r') as f:
                                lines = f.readlines()

                                # Cerca la riga che inizia con "Best Score for Window" e il valore float
                                for line in lines:
                                    for window in n_windows:
                                        if f"Best Score for Window {window}:" in line:
                                            try:
                                                score = float(line.split(":")[1].strip())
                                                best_scores_level_5[subject_key][classifier][window] = score
                                            except ValueError:
                                                print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                            break
    
    return best_scores_level_4, best_scores_level_5

# Definisci il path base e le cartelle dei classificatori
base_path = "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE"
classifiers = ["logistic_regression", "xgboost", "svm"]

# Lista dinamica delle finestre (0-50, 25-75, ..., 250-300)
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiama la funzione per processare i file e ottenere i best scores
best_scores_level_4_single_th_all_classifiers, best_scores_level_5_single_th_all_classifiers = process_txt_files(base_path, classifiers, n_windows)

# Stampa i risultati
print("\033[1mbest_scores_level_4_single_th_all_classifiers.keys()\033[0m:", best_scores_level_4_single_th_all_classifiers.keys())
print("\n\033[1mbest_scores_level_5_single_th_all_classifiers.keys()\033[0m:", best_scores_level_5_single_th_all_classifiers.keys())


In [ ]:
best_scores_level_4_single_th_all_classifiers['th_1'].keys()

In [ ]:
#cd Plots_Sliding_Estimator_MNE


In [ ]:
''' PER SALVARE O CARICARE FILE TERAPISTI'''

#path = /home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/subject_level_concatenations.pkl

#cd Plots_Sliding_Estimator_MNE

#import pickle

# Salvare l'intero dizionario annidato con pickle
#with open('best_scores_level_4_single_th_all_classifiers.pkl', 'wb') as f:
#    pickle.dump(best_scores_level_4_single_th_all_classifiers, f)

# Salvare l'intero dizionario annidato con pickle
#with open('best_scores_level_5_single_th_all_classifiers.pkl', 'wb') as f:
#    pickle.dump(best_scores_level_5_single_th_all_classifiers, f)
    
import pickle 
# Caricare il dizionario salvato con pickle
with open('/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/best_scores_level_4_single_th_all_classifiers.pkl', 'rb') as f:
    best_scores_level_4_single_th_all_classifiers = pickle.load(f)

#import pickle 
# Caricare il dizionario salvato con pickle
with open('/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/best_scores_level_5_single_th_all_classifiers.pkl', 'rb') as f:
    best_scores_level_5_single_th_all_classifiers = pickle.load(f)


In [ ]:
# Stampa o salva i risultati per il livello 4
print(f"\t\t\t\t\033[1mBest Scores Level 4 Single Therapists All Classifiers - Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_4_single_th_all_classifiers keys\033[0m: {best_scores_level_4_single_th_all_classifiers.keys()}")

for th_key, classifier_key in best_scores_level_4_single_th_all_classifiers.items():
    
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    
    for classifier, window_key in classifier_key.items():
        print(f"\033[1mClassifier: {classifier}\033[0m")
        for window, window_value in window_key.items():
            print(f"\033[1m{window}\033[0m: {window_value}")
        print()  # Spazio tra i classificatori

# Stampa o salva i risultati per il livello 5
print(f"\n\n\t\t\t\t\033[1mBest Scores Level 5 Single Therapists All Classifiers - Structure\033[0m:\n")
print(f"\033[1mbest_scores_level_5_single_th_all_classifiers keys\033[0m: {best_scores_level_5_single_th_all_classifiers.keys()}")

for th_key, classifier_key in best_scores_level_5_single_th_all_classifiers.items():
    
    print(f"\n\n\t\t\t\t\033[1mTherapist: {th_key}\033[0m\n")
    
    for classifier, window_key in classifier_key.items():
        print(f"\033[1mClassifier: {classifier}\033[0m")
        for window, window_value in window_key.items():
            print(f"\033[1m{window}\033[0m: {window_value}")
        print()  # Spazio tra i classificatori

        
best_scores_level_4_single_th_all_classifiers['th_1']['logistic_regression'].keys()
#best_scores_level_4_single_th_all_classifiers['th_1']['logistic_regression'].keys()


best_scores_level_4_single_th_all_classifiers['th_1'].keys()

In [ ]:
best_scores_level_4_single_th_all_classifiers['th_1']['logistic_regression'].keys()
#best_scores_level_4_single_th_all_classifiers['th_1']['logistic_regression'].keys()

In [ ]:
best_scores_level_4_single_th_all_classifiers['th_1'].keys()

##### **ALL SINGLE Therapists (TH01-TH16) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 DA COEFF DETAIL DALLE RICOSTRUZIONI DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM)**

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

In [ ]:
import os

def process_txt_files(base_path, classifiers, n_windows):
    best_scores_level_4 = {}
    best_scores_level_5 = {}
    best_scores_level_5_detail = {}  # Nuova variabile per i coefficienti di dettaglio del 5° livello
    
    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(base_path, classifier, "EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params")
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)
                
                # Escludi i file che contengono "invalid_params", "all_th_level_4", o "all_th_level_5"
                if "invalid_params" in file_name or 'all_th_level_4' in file_name or 'all_th_level_5' in file_name:
                    continue
                
                # Determina il livello dal nome del file
                if "_level_approx_4_std" in file_name:
                    level = 'approx_4'
                elif "_level_approx_5_std" in file_name:
                    level = 'approx_5'
                elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                    level = "detail_5"
                else:
                    continue  # Salta il file se non è né livello 4 né livello 5
                
                # Verifica che il file sia per uno specifico soggetto (th_1, th_2, ..., th_15)
                subject = None
                if "th_" in file_name:
                    try:
                        subject = file_name.split("th_")[1].split("_")[0]  # Estrai il numero del soggetto (1-15)
                        subject = int(subject)  # Converte in intero per verificare che sia un numero valido
                        subject_key = f"th_{subject}"  # Se tutto va bene, crea la chiave
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue  # Se c'è un errore, passa al prossimo file
                
                # Se il file è di tipo "approx_4"
                if level == 'approx_4':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_4:
                        best_scores_level_4[subject_key] = {}

                    if classifier not in best_scores_level_4[subject_key]:
                        best_scores_level_4[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_4[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break

                # Se il file è di tipo "approx_5"
                elif level == 'approx_5':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5:
                        best_scores_level_5[subject_key] = {}

                    if classifier not in best_scores_level_5[subject_key]:
                        best_scores_level_5[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break
                
                # Se il file è di tipo "detail_5"
                elif level == 'detail_5':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5_detail:
                        best_scores_level_5_detail[subject_key] = {}

                    if classifier not in best_scores_level_5_detail[subject_key]:
                        best_scores_level_5_detail[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5_detail[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break
    
    return best_scores_level_4, best_scores_level_5, best_scores_level_5_detail

# Definisci il path base e le cartelle dei classificatori
base_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE"
classifiers = ["logistic_regression", "xgboost", "svm"]

# Lista dinamica delle finestre (0-50, 25-75, ..., 250-300)
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiama la funzione per processare i file e ottenere i best scores
best_scores_level_4_single_th_all_classifiers, best_scores_level_5_single_th_all_classifiers, best_scores_level_5_detail_single_th_all_classifiers = process_txt_files(base_path, classifiers, n_windows)

# Stampa i risultati
print("\033[1mbest_scores_level_4_single_th_all_classifiers.keys()\033[0m:", best_scores_level_4_single_th_all_classifiers.keys())
print("\n\033[1mbest_scores_level_5_single_th_all_classifiers.keys()\033[0m:", best_scores_level_5_single_th_all_classifiers.keys())
print("\n\033[1mbest_scores_level_5_detail_single_th_all_classifiers.keys()\033[0m:", best_scores_level_5_detail_single_th_all_classifiers.keys())


In [ ]:
print(best_scores_level_4_single_th_all_classifiers['th_1'].keys())
print()
print(best_scores_level_4_single_th_all_classifiers['th_1']['logistic_regression']['0-50'])
print(best_scores_level_5_single_th_all_classifiers['th_1']['logistic_regression']['0-50'])
print(best_scores_level_5_detail_single_th_all_classifiers['th_1']['logistic_regression']['0-50'])
print()
print(best_scores_level_4_single_th_all_classifiers['th_1']['logistic_regression']['25-75'])
print(best_scores_level_5_single_th_all_classifiers['th_1']['logistic_regression']['25-75'])
print(best_scores_level_5_detail_single_th_all_classifiers['th_1']['logistic_regression']['25-75'])

##### **ALL SINGLE Therapists (TH01-TH16) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER EEG FILTERED 1-20 Hz DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM)**

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)

In [ ]:
import os

def process_txt_files(base_path, classifiers, n_windows):
    
    best_scores_filtered_1_20_all_classifiers_th = {}
    
    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(base_path, classifier, "EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20")
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)
                
                # Escludi i file che contengono "invalid_params", "all_th_level_4", o "all_th_level_5"
                if "invalid_params" in file_name or 'all_th_level_4' in file_name or 'all_th_level_5' in file_name:
                    continue
                
                # Determina il livello dal nome del file
                #if "_level_approx_4_std" in file_name:
                #    level = 'approx_4'
                #elif "_level_approx_5_std" in file_name:
                #    level = 'approx_5'
                #elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                #    level = "detail_5"
                #else:
                #    continue  # Salta il file se non è né livello 4 né livello 5
                
                # Determina il livello dal nome del file
                if "filtered_1_20_std" in file_name:
                    level = 'filtered_1_20'
                else:
                    continue  # Salta il file se non è né livello 4 né livello 5
            
            
                # Verifica che il file sia per uno specifico soggetto (th_1, th_2, ..., th_15)
                subject = None
                if "th_" in file_name:
                    try:
                        subject = file_name.split("th_")[1].split("_")[0]  # Estrai il numero del soggetto (1-15)
                        subject = int(subject)  # Converte in intero per verificare che sia un numero valido
                        subject_key = f"th_{subject}"  # Se tutto va bene, crea la chiave
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue  # Se c'è un errore, passa al prossimo file
                
                # Se il file è di tipo "approx_4"
                if level == 'filtered_1_20':
                    
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_filtered_1_20_all_classifiers_th: 
                        best_scores_filtered_1_20_all_classifiers_th[subject_key] = {}

                    if classifier not in best_scores_filtered_1_20_all_classifiers_th[subject_key]:
                        best_scores_filtered_1_20_all_classifiers_th[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_filtered_1_20_all_classifiers_th[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break

               
    return best_scores_filtered_1_20_all_classifiers_th

# Definisci il path base e le cartelle dei classificatori
base_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE"
classifiers = ["logistic_regression", "xgboost", "svm"]

# Lista dinamica delle finestre (0-50, 25-75, ..., 250-300)
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiama la funzione per processare i file e ottenere i best scores
best_scores_filtered_1_20_all_classifiers_th = process_txt_files(base_path, classifiers, n_windows)

# Stampa i risultati
print("\033[1mbest_scores_filtered_1_20_all_classifiers_th.keys()\033[0m:", best_scores_filtered_1_20_all_classifiers_th.keys())


In [ ]:
#best_scores_filtered_1_20_all_classifiers_th['th_1'].keys()

#dict_keys(['logistic_regression', 'xgboost', 'svm'])


#best_scores_filtered_1_20_all_classifiers_th['th_1']['svm'].keys()

#dict_keys(['0-50', '25-75', '50-100', '75-125', '100-150', '125-175',
#           '150-200', '175-225', '200-250', '225-275', '250-300'])

##### **ALL SINGLE Therapists (TH01-TH15) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DALLE RICOSTRUZIONI DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) PER LA RELATIVA FINESTRA TESTATA - OLD VERSION** 

In [ ]:
print(f"len(all_ths_baseline_accuracy_highest_class_in_fold_level_4): {len(all_ths_baseline_accuracy_highest_class_in_fold_level_4)}")    
print(f"len(all_ths_baseline_accuracy_highest_class_in_fold_level_5): {len(all_ths_baseline_accuracy_highest_class_in_fold_level_5)}")

##### **ALL SINGLE Therapists (TH01-TH16) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX & LEVEL 5 DA COEFF DETAIL DELLE RICOSTRUZIONI DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) PER LA RELATIVA FINESTRA TESTATA** 

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DEL FINESTRE'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

# Definisci una mappa di colori per i classificatori
color_map = {
    'logistic_regression': 'green',
    'xgboost': 'purple',
    'svm': 'blue'
}

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

def plot_best_scores_for_subjects(best_scores_level_dict, level, save_path):
    
    ths_baseline_accuracy_highest_class_in_fold = list()
    
    # Crea la cartella principale 'patient'
    
    #main_save_path = os.path.join(save_path, 'therapist_wavelet_levels')
    main_save_path = os.path.join(save_path, 'wavelet_levels', 'therapists')
    os.makedirs(main_save_path, exist_ok=True)
    
    
    for subject, subj_classifier in best_scores_level_dict.items():
        
        # Crea la directory per il soggetto
        subject_dir = os.path.join(main_save_path, f'single_{subject}')
        os.makedirs(subject_dir, exist_ok=True)

        for classifier, win_scores in subj_classifier.items():
            
            # Estrai le chiavi delle finestre e i punteggi per il classificatore corrente
            windows = list(win_scores.keys())
            scores_list = [win_scores[window] for window in windows]
            
        # Controllo delle labels per il soggetto attuale
        if subject in new_subject_level_concatenations_th:
            
            # Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_th[subject]['labels']
            unique_values, labels_counts = np.unique(labels, return_counts=True)
            num_folds = 5 
            total_labels = np.sum(labels_counts)
            elements_per_fold = total_labels / 5
            rounded_elements_per_fold = math.floor(elements_per_fold)
            class_percentage = labels_counts / total_labels * 100
            highest_class_percentage = max(class_percentage)
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
            ths_baseline_accuracy_highest_class_in_fold.append(baseline_accuracy_highest_class_in_fold)
            
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

        # Inizio del Plot
        plt.figure(figsize=(10, 8))
        plt.subplots_adjust(bottom = 0.25)  # Lascia spazio per la legenda
        
        # Crea etichette per le finestre 
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        # Imposta le etichette principali
        plt.xticks(tick_positions, window_labels)
        
        # Aggiungi i punteggi dei classificatori per ogni finestra
        for classifier in ['logistic_regression', 'xgboost', 'svm']:
            
            if subject in best_scores_level_dict:
                classifier_scores_list = []
                
                for window in windows:
                    score = best_scores_level_dict[subject][classifier].get(window, 0)
                    classifier_scores_list.append(score)
                
                #plt.scatter(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color=color_map[classifier])
                plt.plot(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color=color_map[classifier])
                
        # Configura la legenda per i punteggi dei soggetti
        handles, labels = plt.gca().get_legend_handles_labels()  # Ottieni i handle e le etichette esistenti
        
        custom_lines = [plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10) for classifier in best_scores_level_dict[subject].keys()]
        
        for classifier in best_scores_level_dict[subject].keys():
            
            if classifier in color_map:
                custom_lines.append(plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10))
                
        plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subj {subject}')

        plt.xlabel('Windows (50 samples)', fontweight='bold')
        plt.ylabel('Best Accuracy Score', fontweight='bold')

        # Titolo a seconda del livello
        
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        # Titolo a seconda del livello
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for  Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for  Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for  Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for  Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        
        if level == 'approx_4':
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ + δ range: 0-7.812 Hz)')
            level_str = 'theta'
        elif level == 'approx_5':
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)')
            level_str = 'delta'
        elif level == 'detail_5':  # Gestione del livello di dettaglio
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)')
            level_str = 'theta_strict'
            

        plt.grid(True)
        
        custom_lines = [
            plt.Line2D([0], [0], color='black', linestyle='--', label='End of Prestimulus (50th sample)'),
            plt.Line2D([0], [0], color='red', linestyle='--', label=f'Chance Level for Subj {subject}')
        ]
        
        #plt.legend(['logistic_regression', 'xgboost', 'svm', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
        plt.legend(['logistic regression performance for $i^{{th}}$ Window', 'xgboost performance for $i^{{th}}$ Window', 'svm performance for $i^{{th}}$ Window', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
        
        filename = f'best_scores_subject_{subject}_{level_str}_all_classifiers_window_domain.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.tight_layout()
        #plt.show()
        
        plt.savefig(save_file_path, bbox_inches='tight')
        print(f'\nPlot salvato in: \033[1m{save_file_path}\033[0m\n')
        plt.close()

    return ths_baseline_accuracy_highest_class_in_fold

                
# Esempio di utilizzo

save_path_level_4 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'
save_path_level_5 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'
save_path_level_5_detail = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'


# Esegui la funzione per ogni livello
all_ths_baseline_accuracy_highest_class_in_fold_level_4 = plot_best_scores_for_subjects(best_scores_level_4_single_th_all_classifiers, 'approx_4', save_path_level_4)
all_ths_baseline_accuracy_highest_class_in_fold_level_5 = plot_best_scores_for_subjects(best_scores_level_5_single_th_all_classifiers, 'approx_5', save_path_level_5)
all_ths_baseline_accuracy_highest_class_in_fold_level_5_detail = plot_best_scores_for_subjects(best_scores_level_5_detail_single_th_all_classifiers, 'detail_5', save_path_level_5_detail)


In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DEL TEMPO'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

# Definisci una mappa di colori per i classificatori
color_map = {
    'logistic_regression': 'green',
    'xgboost': 'purple',
    'svm': 'blue'
}

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

def plot_best_scores_for_subjects(best_scores_level_dict, level, save_path):
    
    ths_baseline_accuracy_highest_class_in_fold = list()
    
    # Crea la cartella principale 'patient'
    
    #main_save_path = os.path.join(save_path, 'therapist_wavelet_levels')
    main_save_path = os.path.join(save_path, 'wavelet_levels', 'therapists')
    os.makedirs(main_save_path, exist_ok=True)
    
    
    for subject, subj_classifier in best_scores_level_dict.items():
        
        # Crea la directory per il soggetto
        subject_dir = os.path.join(main_save_path, f'single_{subject}')
        os.makedirs(subject_dir, exist_ok=True)

        for classifier, win_scores in subj_classifier.items():
            
            # Estrai le chiavi delle finestre e i punteggi per il classificatore corrente
            windows = list(win_scores.keys())
            scores_list = [win_scores[window] for window in windows]
            
        # Controllo delle labels per il soggetto attuale
        if subject in new_subject_level_concatenations_th:
            
            # Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_th[subject]['labels']
            unique_values, labels_counts = np.unique(labels, return_counts=True)
            num_folds = 5 
            total_labels = np.sum(labels_counts)
            elements_per_fold = total_labels / 5
            rounded_elements_per_fold = math.floor(elements_per_fold)
            class_percentage = labels_counts / total_labels * 100
            highest_class_percentage = max(class_percentage)
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
            ths_baseline_accuracy_highest_class_in_fold.append(baseline_accuracy_highest_class_in_fold)
            
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

        # Inizio del Plot
        plt.figure(figsize=(10, 8))
        plt.subplots_adjust(bottom = 0.25)  # Lascia spazio per la legenda
        
        # Crea etichette per le finestre 
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        # Imposta le etichette principali
        #plt.xticks(tick_positions, window_labels)
        
        '''PER RAPPRESENTAZIONE NEL DOMINIO DEL TEMPO'''
        plt.xticks(window_mid_points_in_ms, [f'{int(pos)} ms' for pos in window_mid_points_in_ms])
        
        # Aggiungi i punteggi dei classificatori per ogni finestra
        for classifier in ['logistic_regression', 'xgboost', 'svm']:
            
            if subject in best_scores_level_dict:
                classifier_scores_list = []
                
                for window in windows:
                    score = best_scores_level_dict[subject][classifier].get(window, 0)
                    classifier_scores_list.append(score)
                
                #plt.scatter(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color=color_map[classifier])
                plt.plot(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color=color_map[classifier])
                
        # Configura la legenda per i punteggi dei soggetti
        handles, labels = plt.gca().get_legend_handles_labels()  # Ottieni i handle e le etichette esistenti
        
        custom_lines = [plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10) for classifier in best_scores_level_dict[subject].keys()]
        
        for classifier in best_scores_level_dict[subject].keys():
            
            if classifier in color_map:
                custom_lines.append(plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10))
                
        '''PER RAPPRESENTAZIONE NEL DOMINIO DEL TEMPO'''
        # Linea verticale tratteggiata per indicare la fine del prestimolo a 200 ms
        plt.axvline(x=0, color='black', linestyle='--', label='End of Prestimulus (0 ms)')
    
        plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subj {subject}')

        plt.xlabel('Time', fontweight='bold')
        plt.ylabel('Best Accuracy Score', fontweight='bold')

        # Titolo a seconda del livello
        
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        # Titolo a seconda del livello
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for  Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for  Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for  Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for  Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        
        if level == 'approx_4':
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ + δ range: 0-7.812 Hz)')
            level_str = 'theta'
        elif level == 'approx_5':
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)')
            level_str = 'delta'
        elif level == 'detail_5':  # Gestione del livello di dettaglio
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)')
            level_str = 'theta_strict'
            

        plt.grid(True)
        
        custom_lines = [
            plt.Line2D([0], [0], color='black', linestyle='--', label='End of Prestimulus (50th sample)'),
            plt.Line2D([0], [0], color='red', linestyle='--', label=f'Chance Level for Subj {subject}')
        ]
        
        #plt.legend(['logistic_regression', 'xgboost', 'svm', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
        plt.legend(['logistic regression performance for $i^{{th}}$ Window', 'xgboost performance for $i^{{th}}$ Window', 'svm performance for $i^{{th}}$ Window', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
        
        filename = f'best_scores_subject_{subject}_{level_str}_all_classifiers_time_domain.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.tight_layout()
        #plt.show()
        
        plt.savefig(save_file_path, bbox_inches='tight')
        print(f'\nPlot salvato in: \033[1m{save_file_path}\033[0m\n')
        plt.close()

    return ths_baseline_accuracy_highest_class_in_fold

                
# Esempio di utilizzo

save_path_level_4 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'
save_path_level_5 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'
save_path_level_5_detail = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'


# Esegui la funzione per ogni livello
all_ths_baseline_accuracy_highest_class_in_fold_level_4 = plot_best_scores_for_subjects(best_scores_level_4_single_th_all_classifiers, 'approx_4', save_path_level_4)
all_ths_baseline_accuracy_highest_class_in_fold_level_5 = plot_best_scores_for_subjects(best_scores_level_5_single_th_all_classifiers, 'approx_5', save_path_level_5)
all_ths_baseline_accuracy_highest_class_in_fold_level_5_detail = plot_best_scores_for_subjects(best_scores_level_5_detail_single_th_all_classifiers, 'detail_5', save_path_level_5_detail)


In [ ]:
print(all_ths_baseline_accuracy_highest_class_in_fold_level_4)
print()
print(all_ths_baseline_accuracy_highest_class_in_fold_level_5)
print()
print(all_ths_baseline_accuracy_highest_class_in_fold_level_5_detail)

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
# Salvare l'intero dizionario annidato con pickle

'SALVATAGGIO PERFORMANCE TERAPISTI SU TUTTI CLASSIFICATORI PER LIVELLO θ + δ, δ e θ'

import pickle

with open('best_scores_level_4_single_th_all_classifiers.pkl', 'wb') as f:
    pickle.dump(best_scores_level_4_single_th_all_classifiers, f)

with open('best_scores_level_5_single_th_all_classifiers.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_single_th_all_classifiers, f)
    
with open('best_scores_level_5_detail_single_th_all_classifiers.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_detail_single_th_all_classifiers, f)

In [ ]:
'SALVATAGGIO BASELINE ACCURACY LEVEL TERAPISTI SU TUTTI CLASSIFICATORI PER LIVELLO θ + δ, δ e θ'

with open('new_baseline_accuracy_all_subjects_th.pkl', 'wb') as f:
    pickle.dump(all_ths_baseline_accuracy_highest_class_in_fold_level_4, f)

##### **ALL SINGLE Therapists (TH01-TH16) CODE PER PLOTS BEST PERFORMANCES SALVATE PER PER EEG FILTERED 1-20 Hz DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) PER LA RELATIVA FINESTRA TESTATA** 

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DEL FINESTRE'''

#PLOTS 

# UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE! 
#RESULTS DI OGNI CLASSIFICATORE DELLA STESSA FINESTRA PER LO STESSO SINGOLO SOGGETTO!

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni


# Definisci una mappa di colori per i classificatori

#verde scuro 
#rosa fuscia
#azzurro acceso
'''
# Plot con colori personalizzati
plt.plot(x, y1, color='#006400', label='Verde Scuro')
plt.plot(x, y2, color='#FF00FF', label='Rosa Fucsia')
plt.plot(x, y3, color='#00BFFF', label='Azzurro Acceso')
'''


color_map = {
    'logistic_regression': '#006400',
    'xgboost': '#FF00FF',
    'svm': '#00BFFF',
}

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

def plot_best_scores_for_subjects(best_scores_dict, save_path):
    
    # ths_baseline_accuracy_highest_class_in_fold_1_20:
    
    # conterrà una lista di accuracies di baseline per ogni soggetto.
    # Poiché i dati del soggetto rimangono gli stessi per i diversi classificatori,
    # l'accuratezza di baseline calcolata sarà la stessa per tutti e tre i classificatori.
    # Pertanto, si avrà lo stesso valore di baseline_accuracy_highest_class_in_fold per il soggetto,
    # indipendentemente dal classificatore utilizzato
    
    ths_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers = list()
    
    for subject, subj_classifier in best_scores_dict.items():
        
        # Crea la directory per il soggetto
        subject_dir = os.path.join(save_path, f'single_{subject}_filtered_1_20')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        '''OLD VERSION'''
        # Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        #windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #scores_list = [scores[window] for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        # Itera su ciascun classificatore
        for classifier, win_scores in subj_classifier.items():
            
            # Estrai le chiavi delle finestre e i punteggi per il classificatore corrente
            windows = list(win_scores.keys())
            #print(f"\033[1mClassifier: \t\033[1m{classifier}\033[0m")
            #print(f"\033[1mN ° Windows\033[0m: {windows}")

            scores_list = [win_scores[window] for window in windows]
            #print(f"\033[1mBest scores of {classifier} for {subject}\033[0m: {scores_list}\n\n")
            
        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th_1_20:
        
        if subject in new_subject_level_concatenations_th_1_20:
        
            # Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_th_1_20[subject]['labels']
            unique_values, labels_counts = np.unique(labels, return_counts=True)
            num_folds = 5 
            print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")
            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")
            elements_per_fold = total_labels / 5
            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            class_percentage = labels_counts / total_labels * 100
            print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
            print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")
            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            ths_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers.append(baseline_accuracy_highest_class_in_fold)

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

        # Inizio del Plot
        plt.figure(figsize=(10, 8))
        plt.subplots_adjust(bottom = 0.25)  # Lascia spazio per la legenda
        
        # Crea etichette per le finestre 
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        # Imposta le etichette principali
        plt.xticks(tick_positions, window_labels)
        
        # Aggiungi i punteggi dei classificatori per ogni finestra
        for classifier in ['logistic_regression', 'xgboost', 'svm']:
            
            #itero sul grande dizionario annidato che do come argomento alla funzione
            #(i.e., best_scores_1_20_single_th_all_classifiers)
            
            if subject in best_scores_dict:
                classifier_scores_list = []
                
                for window in windows:
                    score = best_scores_dict[subject][classifier].get(window, 0)
                    
                    #classifier_scores_list sarà di lunghezza 3, 
                    #che conterrà i punteggi di best score di ogni classificatore 
                    #per la stessa finestra, 
                    #per l'i-esimo soggetto iterato
                    
                    classifier_scores_list.append(score)
                
                #plt.scatter(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color = color_map[classifier])
                plt.plot(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color = color_map[classifier])
        
        # Configura la legenda per i punteggi dei soggetti
        handles, labels = plt.gca().get_legend_handles_labels()  # Ottieni i handle e le etichette esistenti
        
        # Crea una legenda personalizzata per i classificatori
        custom_lines = [plt.Line2D([0], [0], marker='o', color='w', markerfacecolor = color_map[classifier], markersize=10) for classifier in best_scores_dict[subject].keys()]
        
        for classifier in best_scores_dict[subject].keys():
            
            if classifier in color_map:  # Controlla se il classificatore è presente nel color_map
                custom_lines.append(plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10))
                
        # Legenda per i classificatori sotto l'asse X
        #plt.legend(handles, labels, loc='lower center', bbox_to_anchor=(0.5, -0.15), title='Classifiers', ncol=3)

        # Linea verticale tratteggiata nera per il 50° campione (prestimolo)
        plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')

        # Asterisco per indicare il chance level
        plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label = f'Chance Level for Subj {subject}')

        plt.xlabel('Windows (50 samples)', fontweight='bold')
        plt.ylabel('Best Accuracy Score', fontweight='bold')

        # Titolo per i plots
        #plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - EEG filter 1-20 Hz')    
        
        
        plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG preprocessed 1-20Hz')
        level_str = 'filtered_1_20'
            
        #plt.legend(loc = 'upper center', bbox_to_anchor=(0.5, -0.15), ncol=4)
        plt.grid(True)
        
        # Legenda per pre-stimulus e chance level
        custom_lines = [
            plt.Line2D([0], [0], color='black', linestyle='--', label='End of Prestimulus (50th sample)'),
            plt.Line2D([0], [0], color='red', linestyle='--', label=f'Chance Level for Subj {subject}')
        ]
        #plt.legend(handles=custom_lines, loc='lower center', bbox_to_anchor=(0.5, -0.1), title='Prestimulus & Chance Level', ncol=2)
        #plt.legend(handles=custom_lines, loc='best', title = f'Prestimulus Period & Chance Level Accuracy for {subject}', ncol = 3)
        
        #plt.legend(handles=custom_lines, loc='lower center', bbox_to_anchor=(0.5, -0.1), ncol=2)
        
        plt.legend(['logistic_regression', 'xgboost', 'svm', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
    
        # Salva il plot sul path specifico
        filename = f'best_scores_subject_{subject}_{level_str}_window_domain.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.tight_layout()
        #plt.show()
        plt.savefig(save_file_path, bbox_inches='tight')
        print(f'\nPlot salvato in: \033[1m{save_file_path}\033[0m\n')
        plt.close()

    return ths_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers

                
# Esempio di utilizzo
save_path_th_1_20 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/original_filtered_1_20/therapist_1_20'

# Crea la cartella se non esiste
os.makedirs(save_path_th_1_20, exist_ok=True)

# Esegui la funzione per ogni livello
ths_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers = plot_best_scores_for_subjects(best_scores_filtered_1_20_all_classifiers_th, save_path_th_1_20)


In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DEL TEMPO'''

#PLOTS 

# UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE! 
#RESULTS DI OGNI CLASSIFICATORE DELLA STESSA FINESTRA PER LO STESSO SINGOLO SOGGETTO!

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni


# Definisci una mappa di colori per i classificatori

#verde scuro 
#rosa fuscia
#azzurro acceso
'''
# Plot con colori personalizzati
plt.plot(x, y1, color='#006400', label='Verde Scuro')
plt.plot(x, y2, color='#FF00FF', label='Rosa Fucsia')
plt.plot(x, y3, color='#00BFFF', label='Azzurro Acceso')
'''


color_map = {
    'logistic_regression': '#006400',
    'xgboost': '#FF00FF',
    'svm': '#00BFFF',
}

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

def plot_best_scores_for_subjects(best_scores_dict, save_path):
    
    # ths_baseline_accuracy_highest_class_in_fold_1_20:
    
    # conterrà una lista di accuracies di baseline per ogni soggetto.
    # Poiché i dati del soggetto rimangono gli stessi per i diversi classificatori,
    # l'accuratezza di baseline calcolata sarà la stessa per tutti e tre i classificatori.
    # Pertanto, si avrà lo stesso valore di baseline_accuracy_highest_class_in_fold per il soggetto,
    # indipendentemente dal classificatore utilizzato
    
    ths_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers = list()
    
    for subject, subj_classifier in best_scores_dict.items():
        
        # Crea la directory per il soggetto
        subject_dir = os.path.join(save_path, f'single_{subject}_filtered_1_20')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        '''OLD VERSION'''
        # Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        #windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #scores_list = [scores[window] for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        # Itera su ciascun classificatore
        for classifier, win_scores in subj_classifier.items():
            
            # Estrai le chiavi delle finestre e i punteggi per il classificatore corrente
            windows = list(win_scores.keys())
            #print(f"\033[1mClassifier: \t\033[1m{classifier}\033[0m")
            #print(f"\033[1mN ° Windows\033[0m: {windows}")

            scores_list = [win_scores[window] for window in windows]
            #print(f"\033[1mBest scores of {classifier} for {subject}\033[0m: {scores_list}\n\n")
            
        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th_1_20:
        
        if subject in new_subject_level_concatenations_th_1_20:
        
            # Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_th_1_20[subject]['labels']
            unique_values, labels_counts = np.unique(labels, return_counts=True)
            num_folds = 5 
            print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")
            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")
            elements_per_fold = total_labels / 5
            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            class_percentage = labels_counts / total_labels * 100
            print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
            print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")
            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            ths_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers.append(baseline_accuracy_highest_class_in_fold)

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

        # Inizio del Plot
        plt.figure(figsize=(10, 8))
        plt.subplots_adjust(bottom = 0.25)  # Lascia spazio per la legenda
        
        # Crea etichette per le finestre 
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms
        
        '''PER RAPPRESENTAZIONE NEL DOMINIO FINESTRE'''
        # Imposta le etichette principali
        #plt.xticks(tick_positions, window_labels)
        
        '''PER RAPPRESENTAZIONE NEL DOMINIO DEL TEMPO'''
        plt.xticks(window_mid_points_in_ms, [f'{int(pos)} ms' for pos in window_mid_points_in_ms])
        
        # Aggiungi i punteggi dei classificatori per ogni finestra
        for classifier in ['logistic_regression', 'xgboost', 'svm']:
            
            #itero sul grande dizionario annidato che do come argomento alla funzione
            #(i.e., best_scores_1_20_single_th_all_classifiers)
            
            if subject in best_scores_dict:
                classifier_scores_list = []
                
                for window in windows:
                    score = best_scores_dict[subject][classifier].get(window, 0)
                    
                    #classifier_scores_list sarà di lunghezza 3, 
                    #che conterrà i punteggi di best score di ogni classificatore 
                    #per la stessa finestra, 
                    #per l'i-esimo soggetto iterato
                    
                    classifier_scores_list.append(score)
                
                #plt.scatter(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color = color_map[classifier])
                plt.plot(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color = color_map[classifier])
        
        # Configura la legenda per i punteggi dei soggetti
        handles, labels = plt.gca().get_legend_handles_labels()  # Ottieni i handle e le etichette esistenti
        
        # Crea una legenda personalizzata per i classificatori
        custom_lines = [plt.Line2D([0], [0], marker='o', color='w', markerfacecolor = color_map[classifier], markersize=10) for classifier in best_scores_dict[subject].keys()]
        
        for classifier in best_scores_dict[subject].keys():
            
            if classifier in color_map:  # Controlla se il classificatore è presente nel color_map
                custom_lines.append(plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10))
                
        # Legenda per i classificatori sotto l'asse X
        #plt.legend(handles, labels, loc='lower center', bbox_to_anchor=(0.5, -0.15), title='Classifiers', ncol=3)
        
        '''PER RAPPRESENTAZIONE NEL DOMINIO FINESTRE'''
        # Linea verticale tratteggiata nera per il 50° campione (prestimolo)
        #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        
        '''PER RAPPRESENTAZIONE NEL DOMINIO DEL TEMPO'''
        # Linea verticale tratteggiata per indicare la fine del prestimolo a 200 ms
        plt.axvline(x=0, color='black', linestyle='--', label='End of Prestimulus (0 ms)')        
        
        # Asterisco per indicare il chance level
        plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label = f'Chance Level for Subj {subject}')

        plt.xlabel('Time', fontweight='bold')
        plt.ylabel('Best Accuracy Score', fontweight='bold')

        # Titolo per i plots
        #plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - EEG filter 1-20 Hz')    
        
        
        plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG preprocessed 1-20Hz')
        level_str = 'filtered_1_20'
            
        #plt.legend(loc = 'upper center', bbox_to_anchor=(0.5, -0.15), ncol=4)
        plt.grid(True)
        
        # Legenda per pre-stimulus e chance level
        custom_lines = [
            plt.Line2D([0], [0], color='black', linestyle='--', label='End of Prestimulus (50th sample)'),
            plt.Line2D([0], [0], color='red', linestyle='--', label=f'Chance Level for Subj {subject}')
        ]
        #plt.legend(handles=custom_lines, loc='lower center', bbox_to_anchor=(0.5, -0.1), title='Prestimulus & Chance Level', ncol=2)
        #plt.legend(handles=custom_lines, loc='best', title = f'Prestimulus Period & Chance Level Accuracy for {subject}', ncol = 3)
        
        #plt.legend(handles=custom_lines, loc='lower center', bbox_to_anchor=(0.5, -0.1), ncol=2)
        
        plt.legend(['logistic_regression', 'xgboost', 'svm', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
    
        # Salva il plot sul path specifico
        filename = f'best_scores_subject_{subject}_{level_str}_time_domain.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.tight_layout()
        #plt.show()
        plt.savefig(save_file_path, bbox_inches='tight')
        print(f'\nPlot salvato in: \033[1m{save_file_path}\033[0m\n')
        plt.close()

    return ths_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers

                
# Esempio di utilizzo
save_path_th_1_20 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/original_filtered_1_20/therapist_1_20'

# Crea la cartella se non esiste
os.makedirs(save_path_th_1_20, exist_ok=True)

# Esegui la funzione per ogni livello
ths_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers = plot_best_scores_for_subjects(best_scores_filtered_1_20_all_classifiers_th, save_path_th_1_20)


In [ ]:
!pwd

In [ ]:
print(ths_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers)

In [ ]:
# Salvare l'intero dizionario annidato con pickle

'SALVATAGGIO PERFORMANCE TERAPISTI SU TUTTI CLASSIFICATORI PER LIVELLO θ + δ, δ e θ'

import pickle

with open('best_scores_filtered_1_20_all_classifiers_th.pkl', 'wb') as f:
    pickle.dump(best_scores_filtered_1_20_all_classifiers_th, f)
    
'SALVATAGGIO BASELINE ACCURACY LEVEL TERAPISTI SU TUTTI CLASSIFICATORI PER LIVELLO θ + δ, δ e θ'

with open('new_baseline_accuracy_all_subjects_th_1_20.pkl', 'wb') as f:
    pickle.dump(ths_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers, f)

#### **All Therapists (TH01-THTH20)**

### Plots of **Grand Average Mean** of Best Single Subject's Accuracy Score Performances 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **NEW VERSION**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import os


familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def process_txt_files(base_path, classifiers, n_windows):
    best_scores_level_4 = {}
    best_scores_level_5 = {}
    best_scores_level_5_detail = {}  # Nuova variabile per i coefficienti di dettaglio del 5° livello
    
    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(base_path, classifier, "EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params")
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)
                
                # Escludi i file che contengono "invalid_params", "all_th_level_4", o "all_th_level_5"
                if "invalid_params" in file_name or 'all_th_level_4' in file_name or 'all_th_level_5' in file_name:
                    continue
                
                # Determina il livello dal nome del file
                if "_level_approx_4_std" in file_name:
                    level = 'approx_4'
                elif "_level_approx_5_std" in file_name:
                    level = 'approx_5'
                elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                    level = "detail_5"
                else:
                    continue  # Salta il file se non è né livello 4 né livello 5
                
                # Verifica che il file sia per uno specifico soggetto (th_1, th_2, ..., th_15)
                subject = None
                if "th_" in file_name:
                    try:
                        subject = file_name.split("th_")[1].split("_")[0]  # Estrai il numero del soggetto (1-15)
                        subject = int(subject)  # Converte in intero per verificare che sia un numero valido
                        subject_key = f"th_{subject}"  # Se tutto va bene, crea la chiave
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue  # Se c'è un errore, passa al prossimo file
                
                # Se il file è di tipo "approx_4"
                if level == 'approx_4':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_4:
                        best_scores_level_4[subject_key] = {}

                    if classifier not in best_scores_level_4[subject_key]:
                        best_scores_level_4[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_4[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break

                # Se il file è di tipo "approx_5"
                elif level == 'approx_5':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5:
                        best_scores_level_5[subject_key] = {}

                    if classifier not in best_scores_level_5[subject_key]:
                        best_scores_level_5[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break
                
                # Se il file è di tipo "detail_5"
                elif level == 'detail_5':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5_detail:
                        best_scores_level_5_detail[subject_key] = {}

                    if classifier not in best_scores_level_5_detail[subject_key]:
                        best_scores_level_5_detail[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5_detail[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break
    
    return best_scores_level_4, best_scores_level_5, best_scores_level_5_detail

# Definisci il path base e le cartelle dei classificatori
base_path = f"/home/stefano/Interrogait/{familiar_path}"
classifiers = ["logistic_regression", "xgboost", "svm"]

# Lista dinamica delle finestre (0-50, 25-75, ..., 250-300)
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiama la funzione per processare i file e ottenere i best scores
best_scores_level_4_single_th_all_classifiers, best_scores_level_5_single_th_all_classifiers, best_scores_level_5_detail_single_th_all_classifiers = process_txt_files(base_path, classifiers, n_windows)

# Stampa i risultati
print("\033[1mbest_scores_level_4_single_th_all_classifiers.keys()\033[0m:", best_scores_level_4_single_th_all_classifiers.keys())
print("\n\033[1mbest_scores_level_5_single_th_all_classifiers.keys()\033[0m:", best_scores_level_5_single_th_all_classifiers.keys())
print("\n\033[1mbest_scores_level_5_detail_single_th_all_classifiers.keys()\033[0m:", best_scores_level_5_detail_single_th_all_classifiers.keys())


In [ ]:
print(best_scores_level_4_single_th_all_classifiers['th_20'].keys())
print(best_scores_level_4_single_th_all_classifiers['th_20']['svm']['0-50'])

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA PER OGNI CLASSIFIER - NEW VERSION


Spiegazione delle modifiche

- Parametro classifier nella funzione: La funzione calculate_mean_and_confidence_interval ora 
prende un parametro aggiuntivo classifier, in modo che possa calcolare le statistiche 
per un classificatore specifico all'interno della struttura best_scores.

- Raccolta dei punteggi: All'interno della funzione, per ogni finestra (window), 
raccogli i punteggi di tutti i soggetti per il classificatore specificato.

- Dizionari annidati: statistics_level_4, statistics_level_5 e statistics_level_5_detail sono ora
dizionari annidati, dove ogni classificatore ha il proprio dizionario di risultati per le varie finestre temporali.


Ecco un esempio di come apparirebbe statistics_level_4:

statistics_level_4 = {
    "logistic_regression": {
        "0-50": {
            "mean": 0.78,
            "ci_lower": 0.75,
            "ci_upper": 0.81
        },
        "25-75": {
            "mean": 0.82,
            "ci_lower": 0.79,
            "ci_upper": 0.85
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.76,
            "ci_lower": 0.72,
            "ci_upper": 0.80
        }
    },
    "xgboost": {
        "0-50": {
            "mean": 0.80,
            "ci_lower": 0.77,
            "ci_upper": 0.83
        },
        "25-75": {
            "mean": 0.84,
            "ci_lower": 0.81,
            "ci_upper": 0.87
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.79,
            "ci_lower": 0.75,
            "ci_upper": 0.83
        }
    },
    "svm": {
        "0-50": {
            "mean": 0.77,
            "ci_lower": 0.74,
            "ci_upper": 0.80
        },
        "25-75": {
            "mean": 0.81,
            "ci_lower": 0.78,
            "ci_upper": 0.84
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.75,
            "ci_lower": 0.71,
            "ci_upper": 0.79
        }
    }
}
'''

import numpy as np
import scipy.stats as stats

n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
             "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, classifier, windows, confidence_level=0.95):
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario per un classificatore specifico.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti per il classificatore specificato
        scores = [subject_scores[classifier][window] 
                  for subject_scores in best_scores.values() 
                  if window in subject_scores[classifier]]
        
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per ciascun classificatore nei best scores di livello 4
statistics_level_4 = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_4_single_th_all_classifiers, classifier, n_windows)
    for classifier in ["logistic_regression", "xgboost", "svm"]
}

# Esegui la funzione per ciascun classificatore nei best scores di livello 5
statistics_level_5 = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_5_single_th_all_classifiers, classifier, n_windows)
    for classifier in ["logistic_regression", "xgboost", "svm"]
}

# Esegui la funzione per ciascun classificatore nei best scores di dettaglio di livello 5
statistics_level_5_detail = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_5_detail_single_th_all_classifiers, classifier, n_windows)
    for classifier in ["logistic_regression", "xgboost", "svm"]
}

# Funzione per stampare i risultati con i classificatori in grassetto
def print_bold_statistics(statistics):
    for classifier in statistics:
        print(f"\033[1m{classifier}\033[0m")  # Stampa il nome del classificatore in grassetto
        for window, stats in statistics[classifier].items():
            print(f"  {window}: Mean = {stats['mean']:.2f}, CI Lower = {stats['ci_lower']:.2f}, CI Upper = {stats['ci_upper']:.2f}")

# Stampa i risultati per ciascun livello
print("Risultati per il livello 4:\n")
print_bold_statistics(statistics_level_4)

print("\n\nRisultati per il livello 5:\n")
print_bold_statistics(statistics_level_5)

print("\n\nRisultati per il dettaglio livello 5:\n")
print_bold_statistics(statistics_level_5_detail)

In [ ]:
type(statistics_level_4)

In [ ]:
#cd ..

In [ ]:
!pwd

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_all_th_concat_reconstructions.pkl', 'rb') as f:
    new_all_th_concat_reconstructions = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_th['th_1'].keys()

In [ ]:
new_all_th_concat_reconstructions.keys()

In [ ]:
print(new_all_th_concat_reconstructions['all_th_fourth_labels'].shape)
print(new_all_th_concat_reconstructions['all_th_fifth_labels'].shape)
print(new_all_th_concat_reconstructions['all_th_fifth_detail_labels'].shape)
print()
print(np.unique(new_all_th_concat_reconstructions['all_th_fourth_labels'], return_counts= True))
print(np.unique(new_all_th_concat_reconstructions['all_th_fifth_labels'], return_counts= True))
print(np.unique(new_all_th_concat_reconstructions['all_th_fifth_detail_labels'], return_counts= True))

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW MEAN VERSION - DOMINIO DEL TEMPO

                                                LE WINDOWS SONO DIZIONARI!
                                                
                                                 EEG WAVELET FEATURES
'''

'''
Nell'implementazione attuale, 
le posizioni sull'asse x (window_mid_points_in_ms) rappresentano 
i punti temporali corrispondenti al centro di ciascuna finestra. 

Quindi, ogni etichetta sull'asse x indica la metà temporale della rispettiva finestra in millisecondi.

'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

# Definisci una mappa di colori per i classificatori
color_map = {
    'logistic_regression': 'green',
    'xgboost': 'purple',
    'svm': 'blue'
}

def calculate_chance_level(labels):
    unique_values, labels_counts = np.unique(labels, return_counts=True)
    num_folds = 5 
    total_labels = np.sum(labels_counts)
    elements_per_fold = total_labels / num_folds
    rounded_elements_per_fold = math.floor(elements_per_fold)
    class_percentage = labels_counts / total_labels * 100
    highest_class_percentage = max(class_percentage)
    samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
    exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
    baseline_accuracy = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
    return baseline_accuracy

def plot_mean_best_scores_for_window(statistics_level_dict, level_str, save_path):
    
   # Calcola il livello di chance usando le etichette concatenate in new_all_th_concat_reconstructions
    baseline_accuracy_highest_class_in_fold = calculate_chance_level(all_labels)

    # Crea la cartella principale 'mean_wavelet_levels' dentro 'therapists'
    mean_wavelet_levels_path = os.path.join(save_path, 'mean_wavelet_levels', 'therapists')
    os.makedirs(mean_wavelet_levels_path, exist_ok=True)
    
    # Crea una lista per le finestre
    #n_windows = list(statistics_level_dict[next(iter(statistics_level_dict))]['logistic_regression'].keys())

    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    
    # Inizializzo le medie per ogni classificatore
    mean_scores = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}
    ci_low = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}
    ci_high = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}

    # Per ogni classificatore e finestra, prendi la media e l'intervallo di confidenza dal dizionario
    for classifier in ['logistic_regression', 'xgboost', 'svm']:
        
        for window in n_windows:
            
            # Estrai la media e l'intervallo di confidenza dai dati
            mean_scores[classifier].append(statistics_level_dict[classifier][window]['mean'])
            ci_low[classifier].append(statistics_level_dict[classifier][window]['ci_lower'])
            ci_high[classifier].append(statistics_level_dict[classifier][window]['ci_upper'])
        
        
    # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
    window_starts_samples = []
    window_ends_samples = []
    window_mid_points_samples = []

    # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
    start_sample = 0

    while start_sample + window_size_samples <= n_samples:
        end_sample = start_sample + window_size_samples
        window_starts_samples.append(start_sample)
        window_ends_samples.append(end_sample)
        window_mid_points_samples.append(start_sample + window_size_samples // 2)
        start_sample += stride_samples

    # Conversione dei punti in millisecondi
    window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
    window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
    window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    # Inizio del plot
    plt.figure(figsize=(10, 7))

    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''PER CAMBIO RAPPRESENTAZIONE DA DOMINIO FINESTRE A DOMINIO DEL TEMPO'''
    
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)
    
    plt.xticks(window_mid_points_in_ms, [f'{int(pos)}' for pos in window_mid_points_in_ms])
    plt.tick_params(axis='x', labelsize=12)
    plt.tick_params(axis='y', labelsize=12)
    
    
     # Aggiungi i punteggi medi dei classificatori e gli intervalli di confidenza
    for classifier in ['logistic_regression', 'xgboost', 'svm']:
        plt.plot(window_mid_points_in_ms, mean_scores[classifier], label=f'{classifier}', color=color_map[classifier])
        plt.fill_between(window_mid_points_in_ms, ci_low[classifier], ci_high[classifier], alpha=0.1, color=color_map[classifier])

    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')

    # Traccia la linea orizzontale della chance level
    baseline_accuracy_highest_class_in_fold = calculate_chance_level(all_labels)
    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level')
    
    # Aggiunge il livello di baseline in base al livello specificato
    if level_str == '4':
        plt.title(f"Therapists' Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level_str} - Θ+δ Range")
        plt.ylim(0.28, 0.40)
    elif level_str == '5':
        plt.title(f"Therapists' Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level_str} - δ Range")
        plt.ylim(0.28, 0.40)
    elif level_str == '5_detail':
        plt.title(f"Therapists' Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level_str} - Θ Range")
        plt.ylim(0.28, 0.40)
        
    plt.xlabel('Time (mms)', fontweight='bold', fontsize = 12)
    plt.ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 12)
    
    #plt.legend(loc='best')
    plt.legend(prop={'weight': 'bold', 'size': 9}, loc='best')
    
    plt.grid(True)
    
    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_ths_level_{level_str}_time_domain.png'  # Usa level invece di level_str
    save_file_path = os.path.join(save_path, 'mean_wavelet_levels', 'therapists', filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'Plot salvato in: \033[1m{save_file_path}\033[0m\n')

# Esempio di utilizzo
all_labels = new_all_th_concat_reconstructions['all_th_fourth_labels']
save_path = f'/home/stefano/Interrogait/{familiar_path}/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_4, '4', save_path)
plot_mean_best_scores_for_window(statistics_level_5, '5', save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail, '5_detail', save_path)


##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE EEG FILTERED 1-20 Hz DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) PER LA RELATIVA FINESTRA TESTATA**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
import pickle 


path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'


# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open(f'{path}new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    
    
# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open(f'{path}new_all_th_concat_reconstructions_1_20.pkl', 'rb') as f:
    new_all_th_concat_reconstructions_1_20 = pickle.load(f)
    

In [ ]:
import os


familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def process_txt_files(base_path, classifiers, n_windows):
    
    best_scores_filtered_1_20_all_classifiers_th = {}
    
    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(base_path, classifier, "EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapist_optimized_params_1_20")
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)
                
                # Escludi i file che contengono "invalid_params", "all_th_level_4", o "all_th_level_5"
                if "invalid_params" in file_name or 'all_th_level_4' in file_name or 'all_th_level_5' in file_name:
                    continue
                
                # Determina il livello dal nome del file
                #if "_level_approx_4_std" in file_name:
                #    level = 'approx_4'
                #elif "_level_approx_5_std" in file_name:
                #    level = 'approx_5'
                #elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                #    level = "detail_5"
                #else:
                #    continue  # Salta il file se non è né livello 4 né livello 5
                
                # Determina il livello dal nome del file
                if "filtered_1_20_std" in file_name:
                    level = 'filtered_1_20'
                else:
                    continue  # Salta il file se non è né livello 4 né livello 5
            
            
                # Verifica che il file sia per uno specifico soggetto (th_1, th_2, ..., th_15)
                subject = None
                if "th_" in file_name:
                    try:
                        subject = file_name.split("th_")[1].split("_")[0]  # Estrai il numero del soggetto (1-15)
                        subject = int(subject)  # Converte in intero per verificare che sia un numero valido
                        subject_key = f"th_{subject}"  # Se tutto va bene, crea la chiave
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue  # Se c'è un errore, passa al prossimo file
                
                # Se il file è di tipo "approx_4"
                if level == 'filtered_1_20':
                    
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_filtered_1_20_all_classifiers_th: 
                        best_scores_filtered_1_20_all_classifiers_th[subject_key] = {}

                    if classifier not in best_scores_filtered_1_20_all_classifiers_th[subject_key]:
                        best_scores_filtered_1_20_all_classifiers_th[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_filtered_1_20_all_classifiers_th[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break

               
    return best_scores_filtered_1_20_all_classifiers_th

# Definisci il path base e le cartelle dei classificatori
base_path = f"/home/stefano/Interrogait/{familiar_path}"
classifiers = ["logistic_regression", "xgboost", "svm"]

# Lista dinamica delle finestre (0-50, 25-75, ..., 250-300)
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiama la funzione per processare i file e ottenere i best scores
best_scores_filtered_1_20_all_classifiers_th = process_txt_files(base_path, classifiers, n_windows)

# Stampa i risultati
print("\033[1mbest_scores_filtered_1_20_all_classifiers_th.keys()\033[0m:", best_scores_filtered_1_20_all_classifiers_th.keys())

In [ ]:
print(best_scores_filtered_1_20_all_classifiers_th['th_16']['svm'].keys())
print(best_scores_filtered_1_20_all_classifiers_th['th_16']['svm']['0-50'])

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA PER OGNI CLASSIFIER - NEW VERSION


Spiegazione delle modifiche

- Parametro classifier nella funzione: La funzione calculate_mean_and_confidence_interval ora 
prende un parametro aggiuntivo classifier, in modo che possa calcolare le statistiche 
per un classificatore specifico all'interno della struttura best_scores.

- Raccolta dei punteggi: All'interno della funzione, per ogni finestra (window), 
raccogli i punteggi di tutti i soggetti per il classificatore specificato.

- Dizionari annidati: statistics_level_4, statistics_level_5 e statistics_level_5_detail sono ora
dizionari annidati, dove ogni classificatore ha il proprio dizionario di risultati per le varie finestre temporali.


Ecco un esempio di come apparirebbe statistics_level_4:

statistics_level_4 = {
    "logistic_regression": {
        "0-50": {
            "mean": 0.78,
            "ci_lower": 0.75,
            "ci_upper": 0.81
        },
        "25-75": {
            "mean": 0.82,
            "ci_lower": 0.79,
            "ci_upper": 0.85
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.76,
            "ci_lower": 0.72,
            "ci_upper": 0.80
        }
    },
    "xgboost": {
        "0-50": {
            "mean": 0.80,
            "ci_lower": 0.77,
            "ci_upper": 0.83
        },
        "25-75": {
            "mean": 0.84,
            "ci_lower": 0.81,
            "ci_upper": 0.87
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.79,
            "ci_lower": 0.75,
            "ci_upper": 0.83
        }
    },
    "svm": {
        "0-50": {
            "mean": 0.77,
            "ci_lower": 0.74,
            "ci_upper": 0.80
        },
        "25-75": {
            "mean": 0.81,
            "ci_lower": 0.78,
            "ci_upper": 0.84
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.75,
            "ci_lower": 0.71,
            "ci_upper": 0.79
        }
    }
}
'''

import numpy as np
import scipy.stats as stats

n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
             "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, classifier, windows, confidence_level=0.95):
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario per un classificatore specifico.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti per il classificatore specificato
        scores = [subject_scores[classifier][window] 
                  for subject_scores in best_scores.values() 
                  if window in subject_scores[classifier]]
        
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per ciascun classificatore nei best scores di livello 4
statistics_level_1_20 = {
    classifier: calculate_mean_and_confidence_interval(best_scores_filtered_1_20_all_classifiers_th, classifier, n_windows)
    for classifier in ["logistic_regression", "xgboost", "svm"]
}


# Funzione per stampare i risultati con i classificatori in grassetto
def print_bold_statistics(statistics):
    for classifier in statistics:
        print(f"\033[1m{classifier}\033[0m")  # Stampa il nome del classificatore in grassetto
        for window, stats in statistics[classifier].items():
            print(f"  {window}: Mean = {stats['mean']:.2f}, CI Lower = {stats['ci_lower']:.2f}, CI Upper = {stats['ci_upper']:.2f}")

# Stampa i risultati per ciascun livello
print("Risultati per il livello \033[1mEEG preprocessed 1-20Hz\033[0m:\n")
print_bold_statistics(statistics_level_1_20)

In [ ]:
type(statistics_level_1_20)

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle


path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_subject_level_concatenations_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_th_1_20 = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_all_th_concat_reconstructions_1_20.pkl', 'rb') as f:
    new_all_th_concat_reconstructions_1_20 = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_th_1_20['th_1'].keys()

In [ ]:
new_all_th_concat_reconstructions_1_20.keys()

In [ ]:
print(new_all_th_concat_reconstructions_1_20['labels'].shape)
print()
print(np.unique(new_all_th_concat_reconstructions_1_20['labels'], return_counts= True))

In [ ]:
statistics_level_1_20['svm']['0-50']['ci_upper']

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW MEAN VERSION - DOMINIO DEL TEMPO

Nell'implementazione attuale, 
le posizioni sull'asse x (window_mid_points_in_ms) rappresentano 
i punti temporali corrispondenti al centro di ciascuna finestra. 

Quindi, ogni etichetta sull'asse x indica la metà temporale della rispettiva finestra in millisecondi.

'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

familiar_path = 'New_Plots_Sliding_Estimator_MNE'
    
# Definisci una mappa di colori per i classificatori
color_map = {
    'logistic_regression': '#006400',
    'xgboost': '#FF00FF',
    'svm': '#00BFFF',
}

def calculate_chance_level(labels):
    unique_values, labels_counts = np.unique(labels, return_counts=True)
    num_folds = 5 
    total_labels = np.sum(labels_counts)
    elements_per_fold = total_labels / num_folds
    rounded_elements_per_fold = math.floor(elements_per_fold)
    class_percentage = labels_counts / total_labels * 100
    highest_class_percentage = max(class_percentage)
    samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
    exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
    baseline_accuracy = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
    return baseline_accuracy

def plot_mean_best_scores_for_window(statistics_level_dict, level_str, save_path):
    
   # Calcola il livello di chance usando le etichette concatenate in new_all_th_concat_reconstructions
    baseline_accuracy_highest_class_in_fold = calculate_chance_level(all_labels)

    # Crea la cartella principale 'mean_wavelet_levels' dentro 'therapists'
    mean_filtered_1_20_path = os.path.join(save_path, 'mean_filtered_1_20', 'therapists')
    os.makedirs(mean_filtered_1_20_path, exist_ok=True)
    

    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Inizializzo le medie per ogni classificatore
    mean_scores = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}
    ci_low = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}
    ci_high = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}

    # Per ogni classificatore e finestra, prendi la media e l'intervallo di confidenza dal dizionario
    for classifier in ['logistic_regression', 'xgboost', 'svm']:
        
        for window in n_windows:
            
            # Estrai la media e l'intervallo di confidenza dai dati
            mean_scores[classifier].append(statistics_level_dict[classifier][window]['mean'])
            ci_low[classifier].append(statistics_level_dict[classifier][window]['ci_lower'])
            ci_high[classifier].append(statistics_level_dict[classifier][window]['ci_upper'])
        
        
    # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
    window_starts_samples = []
    window_ends_samples = []
    window_mid_points_samples = []

    # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
    start_sample = 0

    while start_sample + window_size_samples <= n_samples:
        end_sample = start_sample + window_size_samples
        window_starts_samples.append(start_sample)
        window_ends_samples.append(end_sample)
        window_mid_points_samples.append(start_sample + window_size_samples // 2)
        start_sample += stride_samples

    # Conversione dei punti in millisecondi
    window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
    window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
    window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]


    # Inizio del plot
    plt.figure(figsize=(10, 7))

    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''PER CAMBIO RAPPRESENTAZIONE DA DOMINIO FINESTRE A DOMINIO DEL TEMPO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)
    
    plt.xticks(window_mid_points_in_ms, [f'{int(pos)}' for pos in window_mid_points_in_ms])
    
    plt.tick_params(axis='x', labelsize=12)
    plt.tick_params(axis='y', labelsize=12)

     # Aggiungi i punteggi medi dei classificatori e gli intervalli di confidenza
    for classifier in ['logistic_regression', 'xgboost', 'svm']:
        plt.plot(window_mid_points_in_ms, mean_scores[classifier], label=f'{classifier}', color=color_map[classifier])
        plt.fill_between(window_mid_points_in_ms, ci_low[classifier], ci_high[classifier], alpha=0.1, color=color_map[classifier])

    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')

    # Traccia la linea orizzontale della chance level
    baseline_accuracy_highest_class_in_fold = calculate_chance_level(all_labels)
    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level')
    
    # Aggiunge il livello di baseline in base al livello specificato    
    plt.title(f"Therapists' Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG preprocessed 1-20Hz")
    plt.ylim(0.28, 0.43)
    level_str = 'filtered_1_20'
    
    plt.xlabel('Time (mms)', fontweight='bold', fontsize = 12)
    plt.ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 12)
    
    plt.ylim()
    
    #plt.legend(loc='best')
    plt.legend(prop={'weight': 'bold', 'size': 9}, loc='best')
    
    plt.grid(True)
    
    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_ths_level_{level_str}_time_domain.png'  # Usa level invece di level_str
    save_file_path = os.path.join(save_path, 'mean_filtered_1_20', 'therapists', filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'Plot salvato in: \033[1m{save_file_path}\033[0m\n')


# Esempio di utilizzo
all_labels = new_all_th_concat_reconstructions_1_20['labels']
save_path = f'/home/stefano/Interrogait/{familiar_path}/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_1_20, 'filtered_1_20', save_path)

#### **All Therapists (TH01-THTH20)**

### Plots of **Grand Average Mean** of Best Single Subject's Accuracy Score Performances 

#### **Coupled Experimental Conditions**

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **Indicazioni per Codice da Implementare**

Per **ogni soggetto**, tu avrai sostanzialmente **18 file**... che appartengono allo stesso soggetto, ma **riferiti ad un certo livello di ricostruzione del segnale**... i livelli di ricostruzione (che son **3**) son **identificati da** alcune stringhe nel file che son

- **level_approx_4**
- **level_approx_5**
- **level_detail_5**

Ora, queste identificano il livello di ricostruzione utilizzato e fornito al diverso classificatore per l'identificazione dei correlati neurali dei livelli di responsabilità...

Poi, sempre **nella stessa stringa** che compone il **nome del file**, ci sono **altre stringhe** che invece identificano invece la **condizione sperimentale a cui è associato il file**, che son 6, ossia

- baseline_vs_th_resp
- baseline_vs_pt_resp
- baseline_vs_shared_resp
- th_resp_vs_shared_resp
- pt_resp_vs_shared_resp
- th_resp_vs_pt_resp

Queste, invece, identificano sostanzialmente la condizione sperimentale..
Questo vuol dire che, per ogni soggetto, avrò come ti avevo detto 18 file, divisi in 3 gruppi diciamo per il livello di ricostruzione e poi ogni livello di ricostruzione avrà 6 condizioni sperimentali di file associate...

Ora, io vorrei che **i dizionari che mi crei** nel codice che ti ho fornito siano sempre con una simile struttura, dove avrò

Ognuna delle tre variabili vorrei che avesse questa struttura annidata, ossia:

- soggetti (th_)* 
 - classifier, 
  - MA POI va inclusa la chiave che indentifica la "condizione sperimentale" (ossia una tra queste:
    **baseline_vs_th_resp**; **baseline_vs_pt_resp**; **baseline_vs_shared_resp**; **th_resp_vs_shared_resp**;
    **pt_resp_vs_shared_resp**; **th_resp_vs_pt_resp**)  
   - e finestra testata...

Ognuna di queste variabili, vorrei che contenesse secondo questa logica, ossia  
    
**il best score ottenuto sulla specifica finestra, tramite uno specifico classificatore, avendo adottato uno specifico livello di ricostruzione del segnale EEG, per una specifica condizione sperimentale per ogni soggetto**


Quello che deve essere modificato, secondo me, è innanzitutto 

1) la logica di estrazione delle stringhe che identificano per uno stesso soggetto, ossia i suoi dati associati ai tre livelli di ricostruzione, usati poi dentro i diversi classificatori... ossia 

- level_approx_4
- level_approx_5
- level_detail_5

(o forse già c'è sta roba)...

Dopodiché,  deve essere aggiunta anche 

2) la logica per l'identificazione per ogni file della condizione sperimentale associata, in modo da creare poi così le sottochiave associate le condizioni sperimentali... 

Di conseguenza, alla fine dovrei avere **tre dizionari annidati su diversi livelli**, ciascuno che conterrà, 
**per ogni specifico soggetto** (ovviamente ogni dizionario fa riferimento ad un certo livello di ricostruzione utilizzato), **il Best Score** che, ogni soggetto singolarmente, ha ottenuto sulla **specifica finestra**, rispetto al **confronto con una specifica coppia di condizioni sperimentali**, utilizzando uno **specifico classificatore**...



##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **COUPLED EXPERIMENTAL CONDITIONS** 


##### **DA FARE : FARE PLOTS 1 ACCANTO ALL'ALTRO!**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import os

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def process_txt_files(base_path, classifiers, n_windows):
    
    # Dizionari per ogni livello di ricostruzione
    best_scores_level_4 = {}
    best_scores_level_5 = {}
    best_scores_level_5_detail = {}

    # Condizioni sperimentali
    conditions = [
        "baseline_vs_th_resp",
        "baseline_vs_pt_resp",
        "baseline_vs_shared_resp",
        "th_resp_vs_shared_resp",
        "pt_resp_vs_shared_resp",
        "th_resp_vs_pt_resp"
    ]

    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(
            base_path, classifier, 
            "EEG_2_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond"
        )
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            
            if file_name.endswith(".txt"):
                
                file_path = os.path.join(classifier_path, file_name)

                # Determina il livello dal nome del file
                if "_level_approx_4" in file_name:
                    level = 'approx_4'
                    #target_dict = best_scores_level_4
                elif "_level_approx_5" in file_name:
                    level = 'approx_5'
                    #target_dict = best_scores_level_5
                elif "_level_detail_5" in file_name:
                    level = "detail_5"
                    #target_dict = best_scores_level_5_detail
                else:
                    continue  # Salta il file se non è un livello valido

                # Estrai il soggetto
                subject = None
                if "th_" in file_name:
                    try:
                        subject = file_name.split("th_")[1].split("_")[0]
                        subject = int(subject)
                        subject_key = f"th_{subject}"
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue
                
                # Estrai la condizione sperimentale
                condition = None
                for cond in conditions:
                    if cond in file_name:
                        condition = cond
                        break
                if not condition:
                    print(f"Nessuna condizione valida trovata per il file: {file_name}")
                    continue

                # Se il file è di tipo "approx_4"
                if level == 'approx_4':
                    
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_4:
                        best_scores_level_4[subject_key] = {}

                    if classifier not in best_scores_level_4[subject_key]:
                        best_scores_level_4[subject_key][classifier] = {}
                    
                    if condition not in best_scores_level_4[subject_key][classifier]:
                        best_scores_level_4[subject_key][classifier][condition] = {}
                        
                        
                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                
                                if window not in best_scores_level_4[subject_key][classifier][condition]:
                                    best_scores_level_4[subject_key][classifier][condition][window] = {}
                                    
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_4[subject_key][classifier][condition][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break

                # Se il file è di tipo "approx_5"
                elif level == 'approx_5':
                    
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5:
                        best_scores_level_5[subject_key] = {}

                    if classifier not in best_scores_level_5[subject_key]:
                        best_scores_level_5[subject_key][classifier] = {}
                        
                    if condition not in best_scores_level_5[subject_key][classifier]:
                        best_scores_level_5[subject_key][classifier][condition] = {}
                        
                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                
                                if window not in best_scores_level_5[subject_key][classifier][condition]:
                                    best_scores_level_5[subject_key][classifier][condition][window] = {}
                                    
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5[subject_key][classifier][condition][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break
                
                # Se il file è di tipo "detail_5"
                elif level == 'detail_5':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5_detail:
                        best_scores_level_5_detail[subject_key] = {}

                    if classifier not in best_scores_level_5_detail[subject_key]:
                        best_scores_level_5_detail[subject_key][classifier] = {}
                        
                    if condition not in best_scores_level_5_detail[subject_key][classifier]:
                        best_scores_level_5_detail[subject_key][classifier][condition] = {}
                        

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if window not in best_scores_level_5_detail[subject_key][classifier][condition]:
                                    best_scores_level_5_detail[subject_key][classifier][condition][window] = {}
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5_detail[subject_key][classifier][condition][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break


    return best_scores_level_4, best_scores_level_5, best_scores_level_5_detail


# Configurazione dei parametri
base_path = f"/home/stefano/Interrogait/{familiar_path}"

classifiers = ["logistic_regression", "xgboost", "svm"]
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiamata della funzione
best_scores_level_4_th_all_classifiers_coupled_exp, best_scores_level_5_th_all_classifiers_coupled_exp, best_scores_level_5_detail_th_all_classifiers_coupled_exp = process_txt_files(base_path, classifiers, n_windows)

# Output dei risultati
print("\033[1mbest_scores_level_4_th_all_classifiers_coupled_exp.keys()\033[0m:", best_scores_level_4_th_all_classifiers_coupled_exp.keys())
print("\033[1mbest_scores_level_5_th_all_classifiers_coupled_exp.keys()\033[0m:", best_scores_level_5_th_all_classifiers_coupled_exp.keys())
print("\033[1mbest_scores_level_5_detail_th_all_classifiers_coupled_exp.keys()\033[0m:", best_scores_level_5_detail_th_all_classifiers_coupled_exp.keys())


In [ ]:
print(best_scores_level_4_th_all_classifiers_coupled_exp.keys())
print()
print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1'].keys())
print()
print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1']['xgboost'].keys())
print()
print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp'].keys())
print()
print(best_scores_level_4_th_all_classifiers_coupled_exp['th_16']['svm']['baseline_vs_th_resp']['0-50'])

In [ ]:
#print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])
#print()
#print(best_scores_level_5_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])
#print()
#print(best_scores_level_5_detail_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA PER OGNI CLASSIFIER - NEW VERSION


Cosa fa il codice:
Funzione calculate_mean_and_confidence_interval:

Calcola la media e l'intervallo di confidenza per ogni finestra per ogni confronto 
(per esempio, baseline_vs_th_resp, th_resp_vs_pt_resp, etc.) e classificatore.

Raggruppa i risultati per confronto e finestra temporale.
Calcolo delle statistiche:

Per ciascun livello di ricostruzione (4, 5, 5 dettagliato), la funzione calcola le statistiche per ogni classificatore.
Usa il dizionario con i punteggi migliori (best_scores_level_4_th_all_classifiers_coupled_exp, etc.).

Stampa dei risultati:

La funzione print_bold_statistics stampa i risultati per ogni classificatore, 
confronto e finestra con la media e l'intervallo di confidenza.

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 
Filtra i dati:

Per un classificatore specifico (ad esempio logistic_regression, xgboost, svm).
Per una condizione sperimentale specifica (ad esempio baseline_vs_th_resp).
Per una finestra temporale specifica (ad esempio 0-50).
Raccoglie i Best Score di tutti i soggetti:

Esamina i punteggi per la stessa finestra temporale.
Include solo i soggetti che hanno un punteggio per quel classificatore, quella condizione e quella finestra.
Calcola la statistica:

Media dei punteggi raccolti.
Deviazione standard.
Intervallo di confidenza (CI) al livello di confidenza desiderato (default: 95%), utilizzando la distribuzione t di Student.


Il risultato finale sarà un dizionario annidato, organizzato secondo i seguenti livelli:

Classificatore (ad esempio: logistic_regression, xgboost, svm).
Condizione sperimentale (ad esempio: baseline_vs_th_resp, th_resp_vs_pt_resp).
Finestra temporale (ad esempio: 0-50, 25-75).
Statistiche:
mean: la media dei punteggi.
ci_lower: il limite inferiore dell'intervallo di confidenza.
ci_upper: il limite superiore dell'intervallo di confidenza.

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 
STRUTTURA RISULTANTE

{
    "logistic_regression": {
        "baseline_vs_th_resp": {
            "0-50": {"mean": 0.82, "ci_lower": 0.78, "ci_upper": 0.86},
            "25-75": {"mean": 0.85, "ci_lower": 0.81, "ci_upper": 0.89},
            "50-100": {"mean": 0.80, "ci_lower": 0.76, "ci_upper": 0.84},
            ...
        },
        "th_resp_vs_pt_resp": {
            "0-50": {"mean": 0.75, "ci_lower": 0.70, "ci_upper": 0.80},
            "25-75": {"mean": 0.78, "ci_lower": 0.73, "ci_upper": 0.83},
            ...
        },
        ...
    },
    "xgboost": {
        "baseline_vs_th_resp": {
            "0-50": {"mean": 0.88, "ci_lower": 0.84, "ci_upper": 0.92},
            "25-75": {"mean": 0.87, "ci_lower": 0.83, "ci_upper": 0.91},
            ...
        },
        ...
    },
    "svm": {
        ...
    }
}

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 

'''

import numpy as np
import scipy.stats as stats

# Definizione delle finestre temporali
n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
             "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, classifier, windows, comparisons, confidence_level=0.95):
    """
    Calcola la media e l'intervallo di confidenza per ogni finestra e condizione sperimentale 
    per un classificatore specifico e raccoglie i risultati in un dizionario.
    """
    results = {}

    for comparison in comparisons:
        comparison_results = {}  # Risultati per un confronto specifico

        for window in windows:
            
            # Raccogli tutti i best scores per questa finestra da tutti i soggetti per il classificatore specificato
            scores = [subject_scores[classifier][comparison][window] 
                      for subject_scores in best_scores.values() 
                      if comparison in subject_scores[classifier] and window in subject_scores[classifier][comparison]]
            
            if scores:  # Se ci sono punteggi
                # Calcola la media
                mean_score = np.mean(scores)
                
                # Calcola la deviazione standard
                std_dev = np.std(scores, ddof=1)
                
                # Numero di soggetti
                n = len(scores)
                
                # Calcola l'intervallo di confidenza
                confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
                
                # Salva i risultati per la finestra specifica e il confronto
                comparison_results[window] = {
                    'mean': mean_score,
                    'ci_lower': confidence_interval[0],
                    'ci_upper': confidence_interval[1]
                }
        
        # Salva i risultati per il confronto
        results[comparison] = comparison_results

    return results


# Classificatori e confronti da usare

# Configurazione dei parametri

classifiers = ["logistic_regression", "xgboost", "svm"]

comparisons = ['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 
               'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp']

# Calcolare le statistiche per ciascun livello
statistics_level_4_th_fam = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_4_th_all_classifiers_coupled_exp, classifier, n_windows, comparisons)
    for classifier in classifiers
}

statistics_level_5_th_fam = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_5_th_all_classifiers_coupled_exp, classifier, n_windows, comparisons)
    for classifier in classifiers
}

statistics_level_5_detail_th_fam = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_5_detail_th_all_classifiers_coupled_exp, classifier, n_windows, comparisons)
    for classifier in classifiers
}

# Funzione per stampare i risultati con i classificatori in grassetto
def print_bold_statistics(statistics):
    for classifier in statistics:
        print(f"\n\033[1m{classifier}\033[0m\n")  # Stampa il nome del classificatore in grassetto
        for comparison in statistics[classifier]:
            print(f"  \n\033[1m{comparison}\033[0m")  # Stampa il confronto in grassetto
            for window, stats in statistics[classifier][comparison].items():
                print(f"    {window}: Mean = {stats['mean']:.2f}, CI Lower = {stats['ci_lower']:.2f}, CI Upper = {stats['ci_upper']:.2f}")

# Stampa i risultati per ciascun livello
#print("\t\t\tRisultati per il \033[1mlivello 4 coeff approx\033[0m:")
#print_bold_statistics(statistics_level_4_th_fam)

#print("\n\n\t\t\tRisultati per il \033[1mlivello 5 coeff approx\033[0m:")
#print_bold_statistics(statistics_level_5_th_fam)

#print("\n\n\t\t\tRisultati per il \033[1mlivello 5 coeff detail\033[0m:")
#print_bold_statistics(statistics_level_5_detail_th_fam)


In [ ]:
print(best_scores_level_4_th_all_classifiers_coupled_exp.keys())
print()
print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1'].keys())
print()
print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1']['xgboost'].keys())
print()
print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp'].keys())
print()
print(best_scores_level_4_th_all_classifiers_coupled_exp['th_16']['xgboost']['baseline_vs_th_resp']['0-50'])

In [ ]:
type(statistics_level_4_th_fam)

In [ ]:
cd ..

In [ ]:
!pwd

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
print(statistics_level_4_th_fam.keys())
print()
print(statistics_level_4_th_fam['svm'].keys())
print()
print(statistics_level_4_th_fam['svm']['baseline_vs_th_resp'].keys())
print()
print(statistics_level_4_th_fam['svm']['baseline_vs_th_resp']['0-50'].keys())
print()
print(statistics_level_4_th_fam['svm']['baseline_vs_th_resp']['0-50'])

In [ ]:
#Salvo le statitiche di ogni finestra per le mie ricostruzioni  4°, 5° e 4+5° livello  

''' PATH  --> cd Plots_Sliding_Estimator_MNE '''

import pickle


base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'

# Salvare l'intero dizionario annidato con pickle

with open(f'{base_path}/statistics_level_4_th_fam.pkl', 'wb') as f:
    pickle.dump(statistics_level_4_th_fam, f)
    
with open(f'{base_path}/statistics_level_5_th_fam.pkl', 'wb') as f:
    pickle.dump(statistics_level_5_th_fam, f)
    
with open(f'{base_path}/statistics_level_5_detail_th_fam.pkl', 'wb') as f:
    pickle.dump(statistics_level_5_detail_th_fam, f)

In [ ]:
'''               
                        DA QUI IN GIU' BISOGNA UN ATTIMO RAGIONARE! 
    
      DATO CHE IO ORA DOVREI ITERARE RISPETTO A TUTTE LE CONCATENAZIONI MEDIE DI 
      
      OGNI COPPIA DI CONDIZIONI SPERIMETALI CONFRONTATE A COPPIE OSSIA
      
      1) BASELINE_VS_TH_RESP
      2) BASELINE_VS_PT_RESP
      3) BASELINE_VS_SHARED_RESP
      
      4) TH_VS_PT_RESP
      5) TH_VS_SHARED_RESP
      6) PT_RESP_VS_SHARED_RESP
      
      
      ORA, IO HO QUESTE STRUTTURE DATI???
      
      
'''

In [ ]:
cd ..

In [ ]:
cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
!pwd

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''


''' QUESTA VARIABILE NON MI INTERESSA, DATO CHE CONTIENE 
        I DATI CONCATENATI SI', DEL SINGOLO SOGGETTO (CHE MI INTERESSA!),
                    MA PER TUTTE E 4 LE CONDIZIONI SPERIMENTALI INSIEME, OSSIA:
                    
                    1) BASELINE
                    2) TH_RESP
                    3) PT_RESP
                    4) SHARED_RESP
                    
                    ED INVECE A ME INTERESSA PRENDERE
                    I DATI DELLE COPPIE DI CONDIZIONI SPERIMENTALI DEL SINGOLO SOGGETTO!
                    
                    OSSIA
                    
                      1) BASELINE_VS_TH_RESP
                      2) BASELINE_VS_PT_RESP
                      3) BASELINE_VS_SHARED_RESP

                      4) TH_VS_PT_RESP
                      5) TH_VS_SHARED_RESP
                      6) PT_RESP_VS_SHARED_RESP
      
                    
'''    

import pickle


base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_th'''

print(new_subject_level_concatenations_th.keys())
print()
print(new_subject_level_concatenations_th['th_1'].keys())
print()
print(new_subject_level_concatenations_th['th_1']['theta'].shape)

In [ ]:
'''ANCHE QUESTA NON MI INTERESSA, DATO CHE CONTIENE I DATI CONCATENATI, DI TUTTI I SOGGETTI, 
PER TUTTE E 4 LE CONDIZIONI SPERIMENTALI!'''

import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}new_all_th_concat_reconstructions.pkl', 'rb') as f:
    new_all_th_concat_reconstructions = pickle.load(f)  

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_all_th_concat_reconstructions'''

print(new_all_th_concat_reconstructions.keys())
print()
print(new_all_th_concat_reconstructions['all_th_fourth_labels'].shape)

In [ ]:
'''QUESTA, INVECE, POTREBBE DIVENTARE LA VARIABILE DI PARTENZA CHE CI INTERESSA,

DATO CHE CONTIENE I DATI CONCATENATI PER OGNI SOGGETTO,

RISPETTO ALLA COPPIA DI CONDIZIONI SPERIMENTALI CHE STIAMO CONFRONTANDO!!!
'''

import pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}new_subject_level_concatenations_coupled_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th = pickle.load(f)  


In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_coupled_exp_th'''

print(new_subject_level_concatenations_coupled_exp_th.keys())
print()
print(new_subject_level_concatenations_coupled_exp_th['th_1'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['data'].shape)
print()
print(np.unique(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['labels'], return_counts = True))

In [ ]:
'''QUESTA, INVECE, POTREBBE DIVENTARE LA VARIABILE DI PARTENZA CHE CI INTERESSA,

DATO CHE CONTIENE I DATI CONCATENATI PER OGNI SOGGETTO,

RISPETTO ALLA COPPIA DI CONDIZIONI SPERIMENTALI CHE STIAMO CONFRONTANDO!!!
'''

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{base_path}new_subject_level_concatenations_coupled_exp_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th_1_20 = pickle.load(f)  

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_coupled_exp_th'''

print(new_subject_level_concatenations_coupled_exp_th_1_20.keys())
print()
print(new_subject_level_concatenations_coupled_exp_th_1_20['th_1'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp']['data'].shape)
print()
print(np.unique(new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp']['labels'], return_counts = True))

In [ ]:
'''ORA, QUELLO CHE INVECE CI SERVE CREARE, INVECE, 

SAREBBE LA VARIABILE CHE CONCATENA FRA TUTTI I SOGGETTI, I DATI E LE LABELS DELLA CHIAVE CHE IDENTIFICA
LA STESSA CONDIZIONE SPERIMENTALE SULLA QUALE STIAMO ITERANDO AL CICLO CORRENTE DEL FOR LOOP

SIA PER I DATI WAVELET, CHE PER I DATI 1-20!!!


Quindi, per ogni condizione sperimentale,
andiamo a concatenare tutti i dati e le etichette relativi a quella condizione,
ma provenienti da tutti i soggetti. 

Ogni condizione sperimentale ha già i dati e le etichette concatenati per ciascun soggetto,
e ora bisogna unire questi dati da tutti i soggetti per ogni condizione.

Immagina la struttura così:

Condizione sperimentale (per esempio, "condizione_1"):
Unire i dati di tutti i soggetti per la condizione "condizione_1".
Unire le etichette di tutti i soggetti per la condizione "condizione_1".


# La tua struttura dati originale
new_subject_level_concatenations_coupled_exp_th = {
    'subject_1': {
        'theta': {
            'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
            'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        'delta': {
            'condition_1': {'data': np.array([7, 8, 9]), 'labels': np.array([1, 1, 0])},
            'condition_2': {'data': np.array([10, 11, 12]), 'labels': np.array([0, 0, 1])}
        }
    },
    'subject_2': {
        'theta': {
            'condition_1': {'data': np.array([13, 14, 15]), 'labels': np.array([0, 1, 1])},
            'condition_2': {'data': np.array([16, 17, 18]), 'labels': np.array([1, 1, 0])}
        },
        'delta': {
            'condition_1': {'data': np.array([19, 20, 21]), 'labels': np.array([0, 0, 1])},
            'condition_2': {'data': np.array([22, 23, 24]), 'labels': np.array([1, 0, 1])}
        }
    }
}


ATTENZIONE! SICCOME IO ITERO ANCHE RISPETTO AI LIVELLI DI RICOSTRUZIONE, 
LE CONCATENAZIONI VENGANO FATTE PER 3 VOLTE (1 PER CIASCUN LIVELLO)

MA QUESTO RISULTA OVVIAMENTE ERRATO! 

DI CONSEGUENZA, PER CALCOLARE LE LABELS PER OGNI CONDIZIONE SPERIMENTALE, 

SI FA RIFERIMENTO A     "new_all_th_concat_reconstructions_coupled_exp_1_20"

- SIA PER I LIVELLI WAVELET 
- SIA PER IL "LIVELLO" EEG FILTERED 1-20

QUESTO PERCHÉ OVVIAMENTE LE LABELS NON È CHE SI 'RADDOPPIANO' SOLO PER IL FATTO CHE STO CONSIDERANDO
DIVERSI LIVELLI DI RICOSTRUZIONE, MA È SOLO PER TESTARE LE DIFFERENTI PERFORMANCE DI CLASSIFICAZIONE 
RISPETTO AI LIVELLI WAVELET CHE CATTURANO CONTENUTI FREQUENTISTICI DIVERSI! (i.e., θ+δ, θ e δ)

'''

#PER I LIVELLI WAVELET!

import numpy as np

# Nuovo dizionario per i risultati concatenati
new_all_th_concat_reconstructions_coupled_exp = {}

# Iteriamo attraverso tutti i soggetti e per ogni condizione
for subject, subject_data in new_subject_level_concatenations_coupled_exp_th_1_20.items():
    
    for condition, data_labels in subject_data.items():
        
        # Se la condizione non esiste ancora nel dizionario finale, la inizializziamo
        if condition not in new_all_th_concat_reconstructions_coupled_exp:
            new_all_th_concat_reconstructions_coupled_exp[condition] = {
                'data': data_labels['data'],
                'labels': data_labels['labels']
            }
        else:
            # Concatenare i dati e le etichette per la condizione
            new_all_th_concat_reconstructions_coupled_exp[condition]['data'] = np.concatenate(
                (new_all_th_concat_reconstructions_coupled_exp[condition]['data'], data_labels['data'])
            )
            new_all_th_concat_reconstructions_coupled_exp[condition]['labels'] = np.concatenate(
                (new_all_th_concat_reconstructions_coupled_exp[condition]['labels'], data_labels['labels'])
            )

print('Fatto!')
# Verifica dei risultati
#print("Dati concatenati per ciascuna condizione:")
#for condition in new_all_th_concat_reconstructions_coupled_exp:
#    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_th_concat_reconstructions_coupled_exp[condition]['data'].shape}, Shape Etichette: {new_all_th_concat_reconstructions_coupled_exp[condition]['labels'].shape}")
#    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_th_concat_reconstructions_coupled_exp[condition]['labels'], return_counts = True)}")
#    print()
    

# Verifica dei risultati
#print("Dati concatenati per ciascuna condizione:")
#for condition in new_all_th_concat_reconstructions_coupled_exp:
#    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_th_concat_reconstructions_coupled_exp[condition]['data'].shape}, Shape Etichette: {new_all_th_concat_reconstructions_coupled_exp[condition]['labels'].shape}")
#    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_th_concat_reconstructions_coupled_exp[condition]['labels'], return_counts=True)}")
#    
#    print(f"\n\033[4mShape delle etichette per ciascun soggetto nella condizione \033[1m{condition}\033[0m:\033[0m")
#    for subject, subject_data in new_subject_level_concatenations_coupled_exp_th_1_20.items():
#        if condition in subject_data:
#            subject_labels = subject_data[condition]['labels']
#            print(f"- {subject}: {subject_labels.shape}")
#    print()


In [ ]:
print(new_all_th_concat_reconstructions_coupled_exp.keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_th_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_th_resp']['labels'].shape)
print()
print(np.unique(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_th_resp']['labels'], return_counts = True))

In [ ]:
print(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_th_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_pt_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_shared_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['th_resp_vs_pt_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['th_resp_vs_shared_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['pt_resp_vs_shared_resp'].keys())

In [ ]:
print(statistics_level_4_th_fam.keys())
print(statistics_level_4_th_fam['svm'].keys())
print(statistics_level_4_th_fam['svm']['baseline_vs_th_resp'].keys())
print(statistics_level_4_th_fam['svm']['baseline_vs_th_resp']['0-50'].keys())
print(statistics_level_4_th_fam['svm']['baseline_vs_th_resp']['0-50']['mean'])

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **COUPLED EXPERIMENTAL CONDITIONS**

##### **PLOTS DEI TREND DI ACCURATEZZA DI CLASSIFICAZIONE PER OGNI SINGOLO ML CLASSIFIER RISPETTO A TUTTE E 6 LE CONDIZIONI SPERIMENTALI PER LO STESSO LIVELLO WAVELET**

In [ ]:
#import pickle

#FAMILIARI

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'

# Caricare l'intero dizionario annidato con pickle
#with open(f'{fam_path}/statistics_level_4_th_fam.pkl', 'rb') as f:
#    statistics_level_4_th_fam = pickle.load(f)
    

# Caricare l'intero dizionario annidato con pickle
#with open(f'{fam_path}/statistics_level_4_th_fam.pkl', 'rb') as f:
#    statistics_level_4_th_fam = pickle.load(f)
    

#NON FAMILIARI
#unfam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_NF'

# Caricare l'intero dizionario annidato con pickle
#with open(f'{unfam_path}/statistics_level_4_th_unfam.pkl', 'rb') as f:
#    statistics_level_4_th_unfam = pickle.load(f)
    

# Caricare l'intero dizionario annidato con pickle
#with open(f'{unfam_path}/statistics_level_4_pt_unfam.pkl', 'rb') as f:
#    statistics_level_4_pt_unfam = pickle.load(f)
    


In [ ]:
'''
def stampa_media_per_finestra_confronto(svm_stats_1, svm_stats_2):
    """Funzione per stampare la media per ogni finestra in due dizionari di SVM"""
    # Itera sulle chiavi comuni tra i due dizionari (condizioni)
    for condizione in svm_stats_1.keys():
        print(f"\nCondizione: \033[1m{condizione}\033[0m\n")
        
        # Per ogni finestra temporale
        for finestra_temporale in svm_stats_1[condizione].keys():
            # Estrai la media per la finestra per entrambi i gruppi
            media_1 = svm_stats_1[condizione][finestra_temporale]['mean']
            media_2 = svm_stats_2[condizione][finestra_temporale]['mean']
            
            # Stampa la media per la finestra accanto accanto per entrambi i gruppi
            print(f"  Finestra: {finestra_temporale} -> \033[1mMedia TH UNFAM\033[0m: {media_1:.4f} | \033[1mMedia PT UNFAM\033[0m: {media_2:.4f}")
            if media_1 == media_2:
                print('MEDIA UGUALE!')
            else:
                pass
                    
# Confronta i dizionari 'svm' tra i due gruppi
print("Confronto delle medie \033[1mSVM\033[0m:\n")
stampa_media_per_finestra_confronto(statistics_level_4_th_unfam['svm'], statistics_level_4_pt_unfam['svm'])
#stampa_media_per_finestra_confronto(statistics_level_4_th_unfam, statistics_level_4_pt_unfam)
'''

In [ ]:
'''
def stampa_media_per_finestra_confronto_per_classifier(stats_1, stats_2):
    """Funzione per stampare la media per ogni finestra per ogni classifier"""
    
    # Itera su tutti i classifier (es. 'logistic_regression', 'xgboost', 'svm')
    for classifier in stats_1.keys():
        print(f"\nClassifier: \033[1m{classifier}\033[0m")
        
        # Itera sulle chiavi delle condizioni
        for condizione in stats_1[classifier].keys():
            print(f" \nCondizione: \033[1m{condizione}\033[0m")
            
            # Itera su tutte le finestre temporali
            for finestra_temporale in stats_1[classifier][condizione].keys():
                # Estrai la media per la finestra per entrambi i gruppi
                media_1 = stats_1[classifier][condizione][finestra_temporale]['mean']
                media_2 = stats_2[classifier][condizione][finestra_temporale]['mean']
                
                # Stampa la media per la finestra accanto accanto per entrambi i gruppi
                print(f"  Finestra: {finestra_temporale} -> \033[1mMedia TH\033[0m: {media_1:.4f} | \033[1mMedia PT\033[0m: {media_2:.4f}")
                
                if media_1 == media_2:
                    print('MEDIA UGUALE!')
                else:
                    pass
                    
                
# Confronta i dizionari 'svm', 'logistic_regression' e 'xgboost' tra i due gruppi
print("Confronto delle medie per ogni classifier:")
stampa_media_per_finestra_confronto_per_classifier(statistics_level_4_th_fam, statistics_level_4_pt_fam)
'''

In [ ]:
'''PLOTS DEI 6 TREND PER OGNI SINGOLO CLASSIFIER RISPETTO AL LIVELLO DELLA FEATURE WAVELET (4,5,5_detail)

Ecco una versione aggiornata del codice, in cui si va a creare 

Una figura con 2 plots, per ciascun classificatore e ciascun livello di ricostruzione,
mostrando i 6 trend di accuratezza medi di classificazione, 
ciascuno identificante una specifica coppia di condizioni sperimentali. 

Ogni figura include due sottoplot: uno nel dominio delle finestre e uno nel dominio del tempo.

Il codice utilizza colori distintivi per ogni coppia di condizioni sperimentali 
e mantiene la struttura generale di prima, 
aggiungendo la logica per generare i due sottoplot per classificatore e livello.

                                        
                                            CON DOMINIO SOLO DEL TEMPO !!!

'''


import numpy as np
import matplotlib.pyplot as plt
import matplotlib.lines as mlines
import os
import math


# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni


time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)


# Colori per le coppie di condizioni sperimentali
condition_colors = {
    'baseline_vs_th_resp': 'red',
    'baseline_vs_pt_resp': 'blue',
    'baseline_vs_shared_resp': 'green',
    'th_resp_vs_pt_resp': 'orange',
    'th_resp_vs_shared_resp': 'purple',
    'pt_resp_vs_shared_resp': 'deepskyblue'
}

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_level_dict, level_str, save_path):
    
    # Crea la cartella principale 'mean_wavelet_levels' dentro 'therapists'
    mean_wavelet_levels_path = os.path.join(save_path, 'mean_wavelet_levels_2_classes', 'therapists')
    os.makedirs(mean_wavelet_levels_path, exist_ok=True)
    
    # Crea una lista per le finestre
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Inizializzo le medie per ogni classificatore, separati per condizione
    mean_scores = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
                   for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    ci_low = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
              for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    ci_high = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
               for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
    window_starts_samples = []
    window_ends_samples = []
    window_mid_points_samples = []

    # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
    start_sample = 0

    while start_sample + window_size_samples <= n_samples:
        end_sample = start_sample + window_size_samples
        window_starts_samples.append(start_sample)
        window_ends_samples.append(end_sample)
        window_mid_points_samples.append(start_sample + window_size_samples // 2)
        start_sample += stride_samples

    # Conversione dei punti in millisecondi
    window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
    window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
    window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    # Numero di condizioni sperimentali
    conditions = list(statistics_level_dict['logistic_regression'].keys())
            
    # Itera su tutti i classificatori
    for classifier in ['logistic_regression', 'xgboost', 'svm']:
        
        classier_path = os.path.join(mean_wavelet_levels_path, classifier)
        os.makedirs(classier_path, exist_ok=True)
    
        
        # Impostiamo i sottoplot: uno per le finestre e uno per il dominio del tempo
        
        #OPZIONE 1 
        # Crea una nuova figura per ogni classificatore
        
        #plt.figure(figsize=(10, 14))
        #ax1 = plt.subplot(211)  # Sottoplot per il dominio finestre
        #ax2 = plt.subplot(212)  # Sottoplot per il dominio temporale
        
        #OPZIONE 2
        # Crea una nuova figura per ogni classificatore
        
        plt.figure(figsize=(10, 7))
        #ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        #ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale
        
        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        print(f"\t\t\t\t\t\tProcessing classifier: \033[1m{classifier}\033[0m")
        
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        
        #prestimulus_added_ax1 = False
        #prestimulus_added_ax2 = False
        
        prestimulus_added_plt = False
        
        
        # Aggiungi i punteggi medi dei classificatori e gli intervalli di confidenza per ogni condizione
        for condition in conditions:
                
            if condition in statistics_level_dict[classifier].keys():
                
                # Itera sulle finestre e sui punti medi simultaneamente
                for window, mid_point in zip(n_windows, window_mid_points_in_ms):

                    # Recupera i dati relativi alla finestra corrente
                    window_data = statistics_level_dict[classifier][condition].get(window, None)
                    
                    if window_data:
                        
                        # Aggiungi i valori di media e CI intervals alle strutture dati che ho creato
                        mean_best_score = window_data['mean']
                        ci_lower = window_data['ci_lower']
                        ci_upper = window_data['ci_upper']
                        
                        # Popolo le strutture con i valori medi e gli intervalli di confidenza
                        mean_scores[classifier][condition].append(mean_best_score)
                        ci_low[classifier][condition].append(ci_lower)
                        ci_high[classifier][condition].append(ci_upper)
                
                '''
                GESTIONE CON 2 SUBPLOTS
                
                # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
                if level_str == '4':
                    ax1.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ+δ Range", fontsize = 18)
                    ax2.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ+δ Range", fontsize = 18)
                    
                elif level_str == '5':
                    ax1.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - δ Range", fontsize = 18)
                    ax2.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - δ Range", fontsize = 18)

                elif level_str == '5_detail':
                    ax1.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ Range", fontsize = 18)
                    ax2.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ Range", fontsize = 18)
                '''
                
                '''
                GESTIONE CON 1 PLOT SOLO
                '''
                
                # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
                if level_str == '4':
                    plt.title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ+δ Range", fontsize = 12)
                    
                    
                elif level_str == '5':
                    plt.title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - δ Range", fontsize = 12)
                    

                elif level_str == '5_detail':
                    plt.title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ Range", fontsize = 12)
                
                
                '''
                PLOTS CON ASSE NEL DOMINIO DELLE FINESTRE (MA ENTRAMBI ASSIEME)
                
                # Aggiungi la linea di prestimolo solo la prima volta
                if not prestimulus_added_ax1:
                    ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
                    prestimulus_added_ax1 = True
                    
                ax1.plot(window_mid_points_in_ms, mean_scores[classifier][condition], 
                         label=f'{condition}', color=condition_colors[condition])
                
                if level_str == '4':
                    ax1.set_ylim(0.55, 0.68)
                
                elif level_str == '5':
                    ax1.set_ylim(0.55, 0.70)
                
                elif level_str == '5_detail':
                    ax1.set_ylim(0.54, 0.68)
                
                # Imposta le etichette principali per il dominio finestre (ax1)
                ax1.set_xticks(tick_positions)
                ax1.set_xticklabels(window_labels)
                
                # Modifica del fontsize dei tick dell'asse x ed y
                ax1.tick_params(axis='x', labelsize=18)
                ax1.tick_params(axis='y', labelsize=18)

                ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
                ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)
                  
                
                ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
                ax1.grid(True)
                '''
                
    
                '''PLOTS CON ASSE NEL DOMINIO DEL TEMPO (MA ENTRAMBI ASSIEME)
                
                # Aggiungi la linea di prestimolo solo la prima volta
                if not prestimulus_added_ax2:
                    ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
                    prestimulus_added_ax2 = True
                    
        
                ax2.plot(window_mid_points_in_ms, mean_scores[classifier][condition], 
                         label=f'{condition}', color=condition_colors[condition])
                
                if level_str == '4':
                    ax2.set_ylim(0.55, 0.68)
                
                elif level_str == '5':
                    ax2.set_ylim(0.55, 0.70)
                
                elif level_str == '5_detail':
                    ax2.set_ylim(0.54, 0.68)
                
                    
                # Imposta le etichette principali per il dominio temporale (ax2)
                ax2.set_xticks(window_mid_points_in_ms)
                ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])
                
                # Modifica del fontsize dei tick dell'asse x ed y
                ax2.tick_params(axis='x', labelsize=18)
                ax2.tick_params(axis='y', labelsize=18)
        
                ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
                ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)
                
                ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
                ax2.grid(True)
                '''
                
                # Aggiungi il grafico utilizzando plt
                if not prestimulus_added_plt:
                    plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
                    prestimulus_added_plt = True

                plt.plot(window_mid_points_in_ms, mean_scores[classifier][condition], 
                         label=f'{condition}', color=condition_colors[condition])
                
                # Aggiunta dell'intervallo di confidenza
                plt.fill_between(window_mid_points_in_ms, 
                                 ci_low[classifier][condition], 
                                 ci_high[classifier][condition], 
                                 color=condition_colors[condition], 
                                 alpha=0.1)  # Opacità per visualizzare meglio l'intervallo
                
                if level_str == '4':
                    #plt.ylim(0.55, 0.68)
                    plt.ylim(0.52, 0.70)

                elif level_str == '5':
                    #plt.ylim(0.55, 0.70)
                    plt.ylim(0.52, 0.70)
                    
                elif level_str == '5_detail':
                    #plt.ylim(0.54, 0.68)
                    plt.ylim(0.52, 0.70)
                
                # Imposta le etichette principali per il dominio temporale (ax2)
                plt.xticks(window_mid_points_in_ms)
                #plt.ticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])
                
                # Modifica del fontsize dei tick dell'asse x ed y
                plt.tick_params(axis='x', labelsize=12)
                plt.tick_params(axis='y', labelsize=12)

                # Imposta le etichette principali per il dominio temporale
                plt.xticks(window_mid_points_in_ms, [f'{int(pos)}' for pos in window_mid_points_in_ms], fontsize=12)
                plt.xlabel('Time (mms)', fontweight='bold', fontsize=12)
                plt.ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize=12)

                plt.legend(prop={'weight': 'bold', 'size': 8}, loc='best')
                plt.grid(True)

        #plt.show()
        
        # Salva il plot per ogni classificatore
        filename = f'mean_best_scores_{classifier}_level_{level_str}_all_paired_conditions_time_domain_and_conf_interval.png' 
        save_file_path = os.path.join(save_path, 'mean_wavelet_levels_2_classes', 'therapists', classier_path, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[0m\n')

# Esegui per ciascun livello
save_path = f'/home/stefano/Interrogait/{familiar_path}/all_classifiers_plots/EEG_2_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/'

plot_mean_best_scores_for_window(statistics_level_4_th_fam, '4', save_path)
plot_mean_best_scores_for_window(statistics_level_5_th_fam, '5', save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail_th_fam, '5_detail', save_path)


##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **COUPLED EXPERIMENTAL CONDITIONS**

##### **PLOTS DEI TREND DI ACCURATEZZA DI CLASSIFICAZIONE PER OGNI SINGOLO ML CLASSIFIER RISPETTO AD OGNI SINGOLA COPPIA DI CONDIZIONE SPERIMENTALE TESTATA PER TUTTE E 3 LIVELLI WAVELET**

Qui le **figure** sono divise in modo che ****ogni condizione sperimentale****, abbia plottati ****i trend di accuratezza di classificazione****, per la **stessa condizione sperimentale**, per ognuno dei ****3 livelli di ricostruzione del segnale****... 

In questo caso, per maggior visibilità grafica, si impone che, il trend di classificazione tramite lo stesso classificatore per la stessa condizione sperimentale (che ha uno stesso colore) abbia una stile della linea diverso per ogni feature wavelet:

- Livello **approx 4**: **Θ+δ band**
- Livello **approx 5**: **δ band**
- Livello **detail 5**: **Θ band**

In questo modo, si osserva come cambia il rate di discriminabilità rispetto all'uso di una certa wavelet per un certo classificatore, per una determinata condizione sperimentale...



In [ ]:
print(statistics_level_4_th_fam['svm']['baseline_vs_th_resp']['0-50'].keys())
print(statistics_level_4_th_fam['svm']['baseline_vs_th_resp']['0-50']['mean'])

In [ ]:
'''  PLOTS DEI 3 TREND PER OGNI SINGOLO CLASSIFIER PER OGNI CONDIZIONE SPERIMENTALE
RISPETTO AL LIVELLO DELLA FEATURE WAVELET (4,5,5_detail)

Ecco una versione aggiornata del codice, in cui si andrebbe a creare 

Una figura con 2 plots, per ciascun condizione sperimentale e classifier,
mostrando i 3 trend di accuratezza medi di classificazione, 
rispetto alla stessa condizione sperimentale,

rispetto all'uso delle 3 feature wavelet usate

Ogni figura include due sottoplot: uno nel dominio delle finestre e uno nel dominio del tempo.

Il codice utilizza ora invece distintivi per ogni coppia di condizioni sperimentali 
e mantiene la struttura generale di prima, 
aggiungendo la logica per generare i due sottoplot per classificatore e livello.


                                        CON DOMINIO SOLO DEL TEMPO !!!

'''

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.lines as mlines
import os
import math


# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni


time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)


# Colori per le coppie di condizioni sperimentali
condition_colors = {
    'baseline_vs_th_resp': 'red',
    'baseline_vs_pt_resp': 'blue',
    'baseline_vs_shared_resp': 'green',
    'th_resp_vs_pt_resp': 'orange',
    'th_resp_vs_shared_resp': 'purple',
    'pt_resp_vs_shared_resp': 'deepskyblue'
}

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_level_dict, level_str, save_path):
    
    # Crea la cartella principale 'mean_wavelet_levels' dentro 'therapists'
    mean_wavelet_levels_path = os.path.join(save_path, 'mean_wavelet_levels_2_classes', 'therapists')
    os.makedirs(mean_wavelet_levels_path, exist_ok=True)
    
    # Crea una lista per le finestre
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Struttura dati per incorporare statistiche di ogni feature wavelet
    wavelet_levels = {
        'Θ+δ band': statistics_level_4_th_fam, # Theta + Delta feature
        'δ band': statistics_level_5_th_fam, # Delta feature
        'Θ band': statistics_level_5_detail_th_fam # Theta feature
    }

    # Stili di linea per ogni feature
    wavelet_styles = {
        'Θ+δ band': '-',  # Stile tratteggiato per Theta
        'δ band': '--',  # Linea continua per Delta
        'Θ band': ':',  # Linea puntinata per Theta + Delta
    }
    
    
    # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
    window_starts_samples = []
    window_ends_samples = []
    window_mid_points_samples = []

    # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
    start_sample = 0

    while start_sample + window_size_samples <= n_samples:
        end_sample = start_sample + window_size_samples
        window_starts_samples.append(start_sample)
        window_ends_samples.append(end_sample)
        window_mid_points_samples.append(start_sample + window_size_samples // 2)
        start_sample += stride_samples

    # Conversione dei punti in millisecondi
    window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
    window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
    window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    
    # Numero di condizioni sperimentali
    conditions = list(statistics_level_dict['logistic_regression'].keys())
    
    for condition in conditions:
        
        print(f"\t\t\t\tProcessing condition: \033[1m{condition}\033[0m")
        
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        
        #prestimulus_added_ax1 = False
        #prestimulus_added_ax2 = False
        
        prestimulus_added_plt = False
        
        for classifier in ['logistic_regression', 'xgboost', 'svm']:

            # Crea la sotto-cartella principale per il classifier
            classifier_path = os.path.join(save_path, 'mean_wavelet_levels_2_classes', 'therapists', classifier)
            os.makedirs(classifier_path, exist_ok=True)
            
            wavelet_comparisons_path = os.path.join (classifier_path, 'wavelets_comparisons')
            os.makedirs(wavelet_comparisons_path, exist_ok=True)
            
            # Impostiamo i sottoplot: uno per le finestre e uno per il dominio del tempo
        
            #OPZIONE 1 
            # Crea una nuova figura per ogni classificatore

            #plt.figure(figsize=(10, 14))
            #ax1 = plt.subplot(211)  # Sottoplot per il dominio finestre
            #ax2 = plt.subplot(212)  # Sottoplot per il dominio temporale

            #OPZIONE 2
            # Crea una nuova figura per ogni classificatore

            #plt.figure(figsize=(26, 10))
            #ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
            #ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale
        
            plt.figure(figsize=(10, 7))


            # Creiamo le etichette per le finestre
            window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
            tick_positions = window_mid_points_in_ms

            if condition in statistics_level_dict[classifier].keys():
                
                mean_scores_dict = {wavelet_name: [] for wavelet_name in wavelet_levels}
                ci_lower_dict = {wavelet_name: [] for wavelet_name in wavelet_levels}
                ci_upper_dict = {wavelet_name: [] for wavelet_name in wavelet_levels}
                
                # Itera su tutte le wavelet (theta, delta, theta+delta)
                for wavelet_name, wavelet_data in wavelet_levels.items():
                    
                    if condition in wavelet_data[classifier]:
                        for window in n_windows:
                            window_data = wavelet_data[classifier][condition].get(window, None)

                            if window_data:
                                mean_scores_dict[wavelet_name].append(window_data['mean'])
                                ci_lower_dict[wavelet_name].append(window_data['ci_lower'])
                                ci_upper_dict[wavelet_name].append(window_data['ci_upper'])
                    
                    '''
                    
                    PLOTS CON ASSE NEL DOMINIO DELLE FINESTRE (MA ENTRAMBI ASSIEME)
                    
                    # Aggiungi la linea di prestimolo solo la prima volta
                    if not prestimulus_added_ax1:
                        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
                        prestimulus_added_ax1 = True
                    
                    # PLOT DEI TREND DI CLASSIFICAZIONE NEL DOMINIO DELLE FINESTRE E TEMPO
                    
                    
                    # Plotta per ogni wavelet separatamente
                    ax1.plot(window_mid_points_in_ms, mean_scores_dict[wavelet_name], 
                             label=f'{wavelet_name} - {classifier}', color=condition_colors[condition], linestyle=wavelet_styles[wavelet_name])
                    
                    if condition == 'baseline_vs_th_resp': 
                        ax1.set_ylim(0.58, 0.69)
                        
                    elif condition == 'baseline_vs_pt_resp':
                        ax1.set_ylim(0.58, 0.67)
                        
                    elif condition =='baseline_vs_shared_resp':
                        ax1.set_ylim(0.54, 0.66)
                        
                    elif condition =='th_resp_vs_pt_resp':
                        ax1.set_ylim(0.55, 0.65)
                        
                    elif condition =='th_resp_vs_shared_resp':
                        ax1.set_ylim(0.56, 0.67)
                        
                    elif condition =='pt_resp_vs_shared_resp':
                        ax1.set_ylim(0.58, 0.66)
                        
                    # Imposta le etichette principali per il dominio finestre (ax1)
                    ax1.set_xticks(tick_positions)
                    ax1.set_xticklabels(window_labels)
                    
                    # Modifica del fontsize dei tick dell'asse x ed y
                    ax1.tick_params(axis='x', labelsize=16)
                    ax1.tick_params(axis='y', labelsize=16)
                    
                    
                    '''
                    
                    '''
                    PLOTS CON ASSE NEL DOMINIO DELLE TEMPO (MA ENTRAMBI ASSIEME)
                    
                    # Aggiungi la linea di prestimolo solo la prima volta
                    if not prestimulus_added_ax2:
                        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
                        prestimulus_added_ax2 = True

                    ax2.plot(window_mid_points_in_ms, mean_scores_dict[wavelet_name], 
                             label=f'{wavelet_name} - {classifier}', color=condition_colors[condition], linestyle=wavelet_styles[wavelet_name])
                    
                    if condition == 'baseline_vs_th_resp': 
                        ax2.set_ylim(0.58, 0.69)
                        
                    elif condition == 'baseline_vs_pt_resp': 
                        ax2.set_ylim(0.58, 0.67)
                        
                    elif condition =='baseline_vs_shared_resp':
                        ax2.set_ylim(0.54, 0.66)
                        
                    elif condition =='th_resp_vs_pt_resp': 
                        ax2.set_ylim(0.55, 0.65)
                        
                    elif condition =='th_resp_vs_shared_resp': 
                        ax2.set_ylim(0.56, 0.67)
                        
                    elif condition =='pt_resp_vs_shared_resp': 
                        ax2.set_ylim(0.58, 0.66)
                        
                        
                    # Imposta le etichette principali per il dominio temporale (ax2)
                    ax2.set_xticks(window_mid_points_in_ms)
                    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])
                    
                    # Modifica del fontsize dei tick dell'asse x ed y
                    ax2.tick_params(axis='x', labelsize=16)
                    ax2.tick_params(axis='y', labelsize=16)
                    
                    '''
                    
                    # Aggiungi la linea di prestimolo solo la prima volta
                    if not prestimulus_added_plt:
                        plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
                        prestimulus_added_plt = True

                    plt.plot(window_mid_points_in_ms, mean_scores_dict[wavelet_name], 
                             label=f'{wavelet_name} - {classifier}', color=condition_colors[condition], linestyle=wavelet_styles[wavelet_name])
                    
                    if condition == 'baseline_vs_th_resp': 
                        plt.ylim(0.58, 0.69)
                        
                    elif condition == 'baseline_vs_pt_resp': 
                        plt.ylim(0.58, 0.67)
                        
                    elif condition =='baseline_vs_shared_resp':
                        plt.ylim(0.54, 0.66)
                        
                    elif condition =='th_resp_vs_pt_resp': 
                        plt.ylim(0.55, 0.65)
                        
                    elif condition =='th_resp_vs_shared_resp': 
                        plt.ylim(0.56, 0.67)
                        
                    elif condition =='pt_resp_vs_shared_resp': 
                        plt.ylim(0.58, 0.66)
                        
                        
                    # Imposta le etichette principali per il dominio temporale (ax2)
                    plt.xticks(window_mid_points_in_ms)
                    #plt.xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])
                    
                    # Modifica del fontsize dei tick dell'asse x ed y
                    plt.tick_params(axis='x', labelsize=12)
                    plt.tick_params(axis='y', labelsize=12)
                    
                    
                '''
                GESTIONE 2 SUBPLOTS
                
                # Aggiungi il titolo e la legenda
                ax1.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} in {condition} - All Wavelets", fontsize = 14)
                
                ax2.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} in {condition} - All Wavelets", fontsize = 14)
                
                ax1.set_xlabel('Windows (50 samples)', fontweight='bold', fontsize = 18)
                ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 18)
                ax2.set_xlabel('Time (ms)', fontweight='bold', fontsize = 18)
                ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 18)
                
                ax1.legend(prop={'weight': 'bold', 'size': 12}, loc='best')
                ax2.legend(prop={'weight': 'bold', 'size': 12}, loc='best')

                ax1.grid(True)
                ax2.grid(True)

                # Linea del prestimolo
                ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
                ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 ms)')
                
                '''
                # Aggiungi il titolo e la legenda
                plt.title(f"Therapists' Mean Best Accuracy Score for {classifier} in {condition} - All Wavelets", fontsize = 12)
                
                plt.xlabel('Time (ms)', fontweight='bold', fontsize = 12)
                plt.ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 12)
                
                plt.legend(prop={'weight': 'bold', 'size': 9}, loc='best')
                

                plt.grid(True)

                # Linea del prestimolo
                plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 ms)')
                
               
            plt.show()

            # Salva il plot nel percorso specificato
            filename = f'mean_best_scores_{classifier}_all_wavelets_levels_{condition}_time_domain_and_conf_interval.png' 
            save_file_path = os.path.join(save_path, wavelet_comparisons_path, filename)
            #plt.savefig(save_file_path, bbox_inches='tight')
            #plt.close()
            print(f'Plot salvato in: \n\033[1m{save_file_path}\033[0m\n')

# Chiamata delle funzioni con i dati
save_path = f'/home/stefano/Interrogait/{familiar_path}/all_classifiers_plots/EEG_2_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/'

plot_mean_best_scores_for_window(statistics_level_4_th_fam, '4', save_path)
plot_mean_best_scores_for_window(statistics_level_5_th_fam, '5', save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail_th_fam, '5_detail', save_path)

##### **ALL SINGLE Therapists (TH01-TH20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE EEG FILTERED 1-20 Hz DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) PER LA RELATIVA FINESTRA TESTATA**


##### **DA FARE : FARE PLOTS 1 ACCANTO ALL'ALTRO!**


In [ ]:
import os
from collections import OrderedDict

def process_txt_files(base_path, classifiers, n_windows):
    
    # Dizionario per EEG filtered 1-20 Hz
    best_scores_filtered_1_20_all_classifiers_th_coupled_exp = {}

    # Condizioni sperimentali
    conditions = [
        "baseline_vs_th_resp",
        "baseline_vs_pt_resp",
        "baseline_vs_shared_resp",
        "th_resp_vs_shared_resp",
        "pt_resp_vs_shared_resp",
        "th_resp_vs_pt_resp"
    ]

    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(
            base_path, classifier, 
            "EEG_2_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/single_therapist_optimized_params_coupled_exp_cond_1_20"
        )
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)

                # Determina se il file è filtrato
                if "_level_filtered_1_20" not in file_name:
                    continue  # Salta il file se non contiene la stringa desiderata

                # Estrai il soggetto
                subject = None
                if "th_" in file_name:
                    try:
                        subject = file_name.split("th_")[1].split("_")[0]
                        subject = int(subject)
                        subject_key = f"th_{subject}"
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue
                
                # Estrai la condizione sperimentale
                condition = None
                for cond in conditions:
                    if cond in file_name:
                        condition = cond
                        break
                if not condition:
                    print(f"Nessuna condizione valida trovata per il file: {file_name}")
                    continue

                # Crea la struttura del dizionario se non esiste
                if subject_key not in best_scores_filtered_1_20_all_classifiers_th_coupled_exp:
                    best_scores_filtered_1_20_all_classifiers_th_coupled_exp[subject_key] = {}
                if classifier not in best_scores_filtered_1_20_all_classifiers_th_coupled_exp[subject_key]:
                    best_scores_filtered_1_20_all_classifiers_th_coupled_exp[subject_key][classifier] = {}
                if condition not in best_scores_filtered_1_20_all_classifiers_th_coupled_exp[subject_key][classifier]:
                    best_scores_filtered_1_20_all_classifiers_th_coupled_exp[subject_key][classifier][condition] = {}

                # Leggi il file .txt
                with open(file_path, 'r') as f:
                    lines = f.readlines()

                    # Cerca la riga che inizia con "Best Score for Window" e il valore float
                    for line in lines:
                        for window in n_windows:
                            if window not in best_scores_filtered_1_20_all_classifiers_th_coupled_exp[subject_key][classifier][condition]:
                                best_scores_filtered_1_20_all_classifiers_th_coupled_exp[subject_key][classifier][condition][window] = {}
                            if f"Best Score for Window {window}:" in line:
                                try:
                                    score = float(line.split(":")[1].strip())
                                    best_scores_filtered_1_20_all_classifiers_th_coupled_exp[subject_key][classifier][condition][window] = score
                                except ValueError:
                                    print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                break
    
    # Ordina le chiavi del dizionario per numero di soggetto
    best_scores_filtered_1_20_all_classifiers_th_coupled_exp = OrderedDict(
        sorted(best_scores_filtered_1_20_all_classifiers_th_coupled_exp.items(), key=lambda x: int(x[0].split("_")[1]))
    )


    return best_scores_filtered_1_20_all_classifiers_th_coupled_exp

# Configurazione dei parametri
base_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE"
classifiers = ["logistic_regression", "xgboost", "svm"]
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiamata della funzione
best_scores_filtered_1_20_all_classifiers_th_coupled_exp = process_txt_files(base_path, classifiers, n_windows)

# Output dei risultati
print("\033[1mbest_scores_filtered_1_20_all_classifiers_th_coupled_exp.keys()\033[0m:", best_scores_filtered_1_20_all_classifiers_th_coupled_exp.keys())


In [ ]:
print(best_scores_filtered_1_20_all_classifiers_th_coupled_exp.keys())
print()
print(best_scores_filtered_1_20_all_classifiers_th_coupled_exp['th_1'].keys())
print()
print(best_scores_filtered_1_20_all_classifiers_th_coupled_exp['th_1']['xgboost'].keys())
print()
print(best_scores_filtered_1_20_all_classifiers_th_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp'].keys())
print()
print(best_scores_filtered_1_20_all_classifiers_th_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])

In [ ]:
#print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])
#print()
#print(best_scores_level_5_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])
#print()
#print(best_scores_level_5_detail_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA PER OGNI CLASSIFIER - NEW VERSION


Cosa fa il codice:
Funzione calculate_mean_and_confidence_interval:

Calcola la media e l'intervallo di confidenza per ogni finestra per ogni confronto 
(per esempio, baseline_vs_th_resp, th_resp_vs_pt_resp, etc.) e classificatore.

Raggruppa i risultati per confronto e finestra temporale.
Calcolo delle statistiche:

Per ciascun livello di ricostruzione (4, 5, 5 dettagliato), la funzione calcola le statistiche per ogni classificatore.
Usa il dizionario con i punteggi migliori (best_scores_level_4_th_all_classifiers_coupled_exp, etc.).

Stampa dei risultati:

La funzione print_bold_statistics stampa i risultati per ogni classificatore, 
confronto e finestra con la media e l'intervallo di confidenza.

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 
Filtra i dati:

Per un classificatore specifico (ad esempio logistic_regression, xgboost, svm).
Per una condizione sperimentale specifica (ad esempio baseline_vs_th_resp).
Per una finestra temporale specifica (ad esempio 0-50).
Raccoglie i Best Score di tutti i soggetti:

Esamina i punteggi per la stessa finestra temporale.
Include solo i soggetti che hanno un punteggio per quel classificatore, quella condizione e quella finestra.
Calcola la statistica:

Media dei punteggi raccolti.
Deviazione standard.
Intervallo di confidenza (CI) al livello di confidenza desiderato (default: 95%), utilizzando la distribuzione t di Student.


Il risultato finale sarà un dizionario annidato, organizzato secondo i seguenti livelli:

Classificatore (ad esempio: logistic_regression, xgboost, svm).
Condizione sperimentale (ad esempio: baseline_vs_th_resp, th_resp_vs_pt_resp).
Finestra temporale (ad esempio: 0-50, 25-75).
Statistiche:
mean: la media dei punteggi.
ci_lower: il limite inferiore dell'intervallo di confidenza.
ci_upper: il limite superiore dell'intervallo di confidenza.

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 
STRUTTURA RISULTANTE

{
    "logistic_regression": {
        "baseline_vs_th_resp": {
            "0-50": {"mean": 0.82, "ci_lower": 0.78, "ci_upper": 0.86},
            "25-75": {"mean": 0.85, "ci_lower": 0.81, "ci_upper": 0.89},
            "50-100": {"mean": 0.80, "ci_lower": 0.76, "ci_upper": 0.84},
            ...
        },
        "th_resp_vs_pt_resp": {
            "0-50": {"mean": 0.75, "ci_lower": 0.70, "ci_upper": 0.80},
            "25-75": {"mean": 0.78, "ci_lower": 0.73, "ci_upper": 0.83},
            ...
        },
        ...
    },
    "xgboost": {
        "baseline_vs_th_resp": {
            "0-50": {"mean": 0.88, "ci_lower": 0.84, "ci_upper": 0.92},
            "25-75": {"mean": 0.87, "ci_lower": 0.83, "ci_upper": 0.91},
            ...
        },
        ...
    },
    "svm": {
        ...
    }
}

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 

'''

import numpy as np
import scipy.stats as stats

# Definizione delle finestre temporali
n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
             "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, classifier, windows, comparisons, confidence_level=0.95):
    """
    Calcola la media e l'intervallo di confidenza per ogni finestra e condizione sperimentale 
    per un classificatore specifico e raccoglie i risultati in un dizionario.
    """
    results = {}

    for comparison in comparisons:
        comparison_results = {}  # Risultati per un confronto specifico

        for window in windows:
            # Raccogli tutti i best scores per questa finestra da tutti i soggetti per il classificatore specificato
            scores = [subject_scores[classifier][comparison][window] 
                      for subject_scores in best_scores.values() 
                      if comparison in subject_scores[classifier] and window in subject_scores[classifier][comparison]]
            
            if scores:  # Se ci sono punteggi
                # Calcola la media
                mean_score = np.mean(scores)
                
                # Calcola la deviazione standard
                std_dev = np.std(scores, ddof=1)
                
                # Numero di soggetti
                n = len(scores)
                
                # Calcola l'intervallo di confidenza
                confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
                
                # Salva i risultati per la finestra specifica e il confronto
                comparison_results[window] = {
                    'mean': mean_score,
                    'ci_lower': confidence_interval[0],
                    'ci_upper': confidence_interval[1]
                }
        
        # Salva i risultati per il confronto
        results[comparison] = comparison_results

    return results


# Classificatori e confronti da usare
classifiers = ["logistic_regression", "xgboost", "svm"]
comparisons = ['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 
               'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp']

# Calcolare le statistiche per ciascun livello
statistics_level_1_20 = {
    classifier: calculate_mean_and_confidence_interval(best_scores_filtered_1_20_all_classifiers_th_coupled_exp, classifier, n_windows, comparisons)
    for classifier in classifiers
}


# Funzione per stampare i risultati con i classificatori in grassetto
def print_bold_statistics(statistics):
    for classifier in statistics:
        print(f"\n\033[1m{classifier}\033[0m\n")  # Stampa il nome del classificatore in grassetto
        for comparison in statistics[classifier]:
            print(f"  \n\033[1m{comparison}\033[0m")  # Stampa il confronto in grassetto
            for window, stats in statistics[classifier][comparison].items():
                print(f"    {window}: Mean = {stats['mean']:.2f}, CI Lower = {stats['ci_lower']:.2f}, CI Upper = {stats['ci_upper']:.2f}")

# Stampa i risultati per ciascun livello
print("\t\t\tRisultati per il \033[1mlivello EEG 1-20Hz\033[0m:")
print_bold_statistics(statistics_level_1_20)

In [ ]:
type(statistics_level_1_20)

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
print(statistics_level_1_20.keys())
print()
print(statistics_level_1_20['svm'].keys())
print()
print(statistics_level_1_20['svm']['baseline_vs_th_resp'].keys())
print()
print(statistics_level_1_20['svm']['baseline_vs_th_resp']['0-50'].keys())

In [ ]:
'''               
                        DA QUI IN GIU' BISOGNA UN ATTIMO RAGIONARE! 
    
      DATO CHE IO ORA DOVREI ITERARE RISPETTO A TUTTE LE CONCATENAZIONI MEDIE DI 
      
      OGNI COPPIA DI CONDIZIONI SPERIMETALI CONFRONTATE A COPPIE OSSIA
      
      1) BASELINE_VS_TH_RESP
      2) BASELINE_VS_PT_RESP
      3) BASELINE_VS_SHARED_RESP
      
      4) TH_VS_PT_RESP
      5) TH_VS_SHARED_RESP
      6) PT_RESP_VS_SHARED_RESP
      
      
      ORA, IO HO QUESTE STRUTTURE DATI???
      
      
'''

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
!pwd

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''


''' QUESTA VARIABILE NON MI INTERESSA, DATO CHE CONTIENE 
        I DATI CONCATENATI SI', DEL SINGOLO SOGGETTO (CHE MI INTERESSA!),
                    MA PER TUTTE E 4 LE CONDIZIONI SPERIMENTALI INSIEME, OSSIA:
                    
                    1) BASELINE
                    2) TH_RESP
                    3) PT_RESP
                    4) SHARED_RESP
                    
                    ED INVECE A ME INTERESSA PRENDERE
                    I DATI DELLE COPPIE DI CONDIZIONI SPERIMENTALI DEL SINGOLO SOGGETTO!
                    
                    OSSIA
                    
                      1) BASELINE_VS_TH_RESP
                      2) BASELINE_VS_PT_RESP
                      3) BASELINE_VS_SHARED_RESP

                      4) TH_VS_PT_RESP
                      5) TH_VS_SHARED_RESP
                      6) PT_RESP_VS_SHARED_RESP
      
                    
'''    

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_th.pkl', 'rb') as f:
    new_subject_level_concatenations_th = pickle.load(f)

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_th'''

print(new_subject_level_concatenations_th.keys())
print()
print(new_subject_level_concatenations_th['th_1'].keys())
print()
print(new_subject_level_concatenations_th['th_1']['theta'].shape)

In [ ]:
'''ANCHE QUESTA NON MI INTERESSA, DATO CHE CONTIENE I DATI CONCATENATI, DI TUTTI I SOGGETTI, 
PER TUTTE E 4 LE CONDIZIONI SPERIMENTALI!'''

# Caricare l'intero dizionario annidato con pickle
with open('new_all_th_concat_reconstructions.pkl', 'rb') as f:
    new_all_th_concat_reconstructions = pickle.load(f)  

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_all_th_concat_reconstructions'''

print(new_all_th_concat_reconstructions.keys())
print()
print(new_all_th_concat_reconstructions['all_th_fourth_labels'].shape)

In [ ]:
'''QUESTA, INVECE, POTREBBE DIVENTARE LA VARIABILE DI PARTENZA CHE CI INTERESSA,

DATO CHE CONTIENE I DATI CONCATENATI PER OGNI SOGGETTO,

RISPETTO ALLA COPPIA DI CONDIZIONI SPERIMENTALI CHE STIAMO CONFRONTANDO!!!
'''

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th = pickle.load(f)  


In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_coupled_exp_th'''

print(new_subject_level_concatenations_coupled_exp_th.keys())
print()
print(new_subject_level_concatenations_coupled_exp_th['th_1'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_th['th_1']['theta'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_th_resp']['data'].shape)
print()
print(np.unique(new_subject_level_concatenations_coupled_exp_th['th_1']['theta']['baseline_vs_pt_resp']['labels'], return_counts = True))

In [ ]:
'''QUESTA, INVECE, POTREBBE DIVENTARE LA VARIABILE DI PARTENZA CHE CI INTERESSA,

DATO CHE CONTIENE I DATI CONCATENATI PER OGNI SOGGETTO,

RISPETTO ALLA COPPIA DI CONDIZIONI SPERIMENTALI CHE STIAMO CONFRONTANDO!!!
'''

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_th_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_th_1_20 = pickle.load(f)  

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_coupled_exp_th'''

print(new_subject_level_concatenations_coupled_exp_th_1_20.keys())
print()
print(new_subject_level_concatenations_coupled_exp_th_1_20['th_1'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp']['data'].shape)
print()
print(np.unique(new_subject_level_concatenations_coupled_exp_th_1_20['th_1']['baseline_vs_th_resp']['labels'], return_counts = True))

In [ ]:
'''ORA, QUELLO CHE INVECE CI SERVE CREARE, INVECE, 

SAREBBE LA VARIABILE CHE CONCATENA FRA TUTTI I SOGGETTI, I DATI E LE LABELS DELLA CHIAVE CHE IDENTIFICA
LA STESSA CONDIZIONE SPERIMENTALE SULLA QUALE STIAMO ITERANDO AL CICLO CORRENTE DEL FOR LOOP

SIA PER I DATI WAVELET, CHE PER I DATI 1-20!!!


Quindi, per ogni condizione sperimentale,
andiamo a concatenare tutti i dati e le etichette relativi a quella condizione,
ma provenienti da tutti i soggetti. 

Ogni condizione sperimentale ha già i dati e le etichette concatenati per ciascun soggetto,
e ora bisogna unire questi dati da tutti i soggetti per ogni condizione.

Immagina la struttura così:

Condizione sperimentale (per esempio, "condizione_1"):
Unire i dati di tutti i soggetti per la condizione "condizione_1".
Unire le etichette di tutti i soggetti per la condizione "condizione_1".


# La tua struttura dati originale 1_20
new_subject_level_concatenations_coupled_exp_th = {
    'subject_1': {
        'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
        'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        '
    'subject_2': {
        'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
        'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        
    subject_3': {
        'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
        'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        
    }
}


ATTENZIONE! SICCOME IO ITERO ANCHE RISPETTO AI LIVELLI DI RICOSTRUZIONE, 
LE CONCATENAZIONI VENGANO FATTE PER 3 VOLTE (1 PER CIASCUN LIVELLO)

MA QUESTO RISULTA OVVIAMENTE ERRATO! 

DI CONSEGUENZA, PER CALCOLARE LE LABELS PER OGNI CONDIZIONE SPERIMENTALE, 

SI FA RIFERIMENTO A     "new_all_th_concat_reconstructions_coupled_exp_1_20"

- SIA PER I LIVELLI WAVELET 
- SIA PER IL "LIVELLO" EEG FILTERED 1-20

QUESTO PERCHÉ OVVIAMENTE LE LABELS NON È CHE SI 'RADDOPPIANO' SOLO PER IL FATTO CHE STO CONSIDERANDO
DIVERSI LIVELLI DI RICOSTRUZIONE, MA È SOLO PER TESTARE LE DIFFERENTI PERFORMANCE DI CLASSIFICAZIONE 
RISPETTO AI LIVELLI WAVELET CHE CATTURANO CONTENUTI FREQUENTISTICI DIVERSI! (i.e., θ+δ, θ e δ)

'''

#PER I EEG FILTERED 1-20 Hz!

import numpy as np

# Nuovo dizionario per i risultati concatenati
new_all_th_concat_reconstructions_coupled_exp_1_20 = {}

# Iteriamo attraverso tutti i soggetti e per ogni condizione
for subject, subject_data in new_subject_level_concatenations_coupled_exp_th_1_20.items():
    
    for condition, data_labels in subject_data.items():
        
        # Se la condizione non esiste ancora nel dizionario finale, la inizializziamo
        if condition not in new_all_th_concat_reconstructions_coupled_exp_1_20:
            new_all_th_concat_reconstructions_coupled_exp_1_20[condition] = {
                'data': data_labels['data'],
                'labels': data_labels['labels']
            }
        else:
            # Concatenare i dati e le etichette per la condizione
            new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['data'] = np.concatenate(
                (new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['data'], data_labels['data'])
            )
            new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['labels'] = np.concatenate(
                (new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['labels'], data_labels['labels'])
            )

# Verifica dei risultati
#print("Dati concatenati per ciascuna condizione:")
#for condition in new_all_th_concat_reconstructions_coupled_exp_1_20:
#    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['data'].shape}, Shape Etichette: {new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['labels'].shape}")
#    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['labels'], return_counts = True)}")
#    print()

# Verifica dei risultati
print("Dati concatenati per ciascuna condizione:")
for condition in new_all_th_concat_reconstructions_coupled_exp_1_20:
    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['data'].shape}, Shape Etichette: {new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['labels'].shape}")
    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['labels'], return_counts=True)}")
    
    print(f"\n\033[4mShape delle etichette per ciascun soggetto nella condizione \033[1m{condition}\033[0m:\033[0m")
    for subject, subject_data in new_subject_level_concatenations_coupled_exp_th_1_20.items():
        if condition in subject_data:
            subject_labels = subject_data[condition]['labels']
            print(f"- {subject}: {subject_labels.shape}")
    print()

In [ ]:
print(statistics_level_1_20.keys())
print(statistics_level_1_20['svm'].keys())
print(statistics_level_1_20['svm']['baseline_vs_th_resp'].keys())
print(statistics_level_1_20['svm']['baseline_vs_th_resp']['0-50'].keys())

#### **ALL SINGLE Patients (PT01-PT20)**

#### Plots of **EACH SINGLE Subject's Accuracy Score Performances** 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

#### **Istruzioni del codice qui sotto**

##### **Descrizione degli step nel codice per estrarre dalle relative paths dei vari modelli (i.e., LOGISTIC REGRESSION, XGBOOST, SVM) le best score performances salvate per il level 4 e 5 dalle ricostruzioni**:

Fammi un codice python che faccia queste cose 

- **1)** Entrami in una **folder path** (che ti fornisco io) ed iteri in quella folder path

che sarà questa

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/"

qui troverai 3 cartelle, una che si chiama 'logistic_regression' una 'xgboost' ed una 'svm', 
dentro ognuna troverai questo sotto-path (uguale per tutte)

"/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/" al cui interno poi troverai
due cartelle (uguali per tutte e tre):

single_therapists_optimized_params
single_patients_optimized_params

voglio che entri, per ognuna delle 3 cartelle (i.e. una che si chiama 'logistic_regression' una 'xgboost' ed una 'svm’), quindi a questo livello di path

/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression
/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/xgboost
/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/svm

dentro la relativa sotto cartella "single_therapists_optimized_params" quindi dovrai entrare dentro ciascuna sotto-path che ti metto qui sotto

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

- **2)** Vedi se dentro ognuna di queste 3 sotto-path sopra, dentro la cartella "single_therapists_optimized_params" ci siano **file che finiscono con .txt**: 

- **3)** Per ogni file, vedi se contiene la stringa 
**"invalid_params"** 

e se incontri questa stringa, **escludi quei file .txt** e continua.. 

- **4)** Vedi invece se il file contiene la stringa **"optimized_params"** e **"_level_4_std"** o **"optimized_params"** **"_level_5_std**:

- - **4.1.)** In quel caso, entri dentro quel file e **leggilo** ma poi fai una ulteriore considerazione, ossia 
- - vedi se quello che precede "_level_4_std" o "_level_5_std" sia **" th_"** dove * è un **suffisso dinamico**, che va da
1 a 15...

Quindi avrai per ogni soggetto, due file .txt, che finiranno con questa stringa 

Per il **soggetto 1**: "**th_1_level_4_std**" o "**th_1_level_5_std**" 
Per il **soggetto 2**: "**th_2_level_4_std**" o "**th_2_level_5_std**" 

E così via, fino al 15° soggetto...

Di conseguenza, per ogni sotto-path che ti metto qui sotto

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

dovrai entrare dentro le coppie di file .txt relative allo stesso soggetto, per i due livelli di ricostruzione del segnale. 

Di conseguenza entrerai in totale, per il soggetto 'th_1' ad esempio dentro i suoi 6 relativi file, che trovi a coppie dentro le relative sotto-path che ti ho detto sopra , che son

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

- **5)** A quel punto, vedi in ognuna delle coppie di file .txt dentro la relativa sotto-path dello stesso soggetto

(i.e., ossia per esempio avrai per il soggetto 1 due file .txt, che finiranno con questa stringa 

"th_1_level_4_std" o "th_1_level_5_std" )

- **7)** Leggi il file .txt e vedi se ci sia un **riga in quel file .txt** con scritto 

**"Best Score for Window"**, seguito da **una sequenza di stringhe dinamica**, che cambia e che può essere presa da una lista di stringhe iterativamente che si costruisce a priori, del tipo:

"0-50" "25-75" etc., ossia che cambia di 25 valori ogni volta in maniera uniforme, quindi proseguendo sarebbe:
"50-100" "75-125" "100-150" "125-175" "150-200" "175-225" "200-250" "225-275" "250-300"

Quindi la lista di stringa dinamica potrebbe essere

**n_windows** = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"]

di conseguenza, itera per ogni elemento di questa lista "n_windows" per riconoscere se questa **sequenza di stringa dinamica** completi un riga dentro il file .txt che avrà scritto quindi:

**"Best Score for Window" + {elemento della lista "n_windows}**:"

A questo punto, avrai l'intera riga che sarà ad esempio:

"Best Score for Window 0-50: ".. 

In quella stessa riga del file .txt, dovresti trovare un **valore float**.. 

- **8)** Vorrei che prendessi quel valore float e **lo appendessi ad un dizionario**, che conterrà nei suoi vari valori i vari **best score ottenuti da quel soggetto lì, per lo specifico classificatore per ciascuna delle finestra considerate** , 
(che vanno da 0-50 a 250-300, ossia prendendo a riferimento quello che c'è dentro "n_windows"

'n_windows = [ "0-50", "25-75", "50-100" ,"75-125" ,"100-150", "125-175", "150-200", "175-225", "200-250" ,"225-275" ,"250-300"])

Questo dizionario lo chiamerò ad esempio **"best_scores_level_4_single_th"**, che ad esempio avrà, 

come primo "valore", la chiave di altro dizionario, associata alla stringa che si riferisce al soggetto iterato (th_1, th_2 etc) 

e come valore ci sarà un altro dizionario, 

che avrà come chiave il nome della stringa che si riferisce al classificatore testato per quel soggetto lì, 
e che si riferisce al folder del relativo classificatore, (i.e., una volta sarà **logistic_regression**, una volta sarà **xgboost** e una volta sarà **svm**) 

dentro poi ogni sotto-sotto-chiave, ci sarà poi un altro dizionario ancora, che avrà 

- - **A)** come sotto-sotto-sotto-chiave il nome dell'elemento iterato rispetto a "n_windows" e 
- - **B)** come sotto-sotto-sotto-valore il valore float associato al best score trovato per quella finestra lì, per quel soggetto lì, per quel classificatore lì, del tipo

per il sottodizioario **logistic_regression** in riferimento al soggetto ad esempio "th_1":

{*logistic_regression*}: { {'**0-50**': valore float del best score ottenuto dal soggetto 1 sulla finestra 0-50, }
{’25-75’: valore float del best score ottenuto dal soggetto 1 sulla finestra 25-75... etc] }

per **xgboost** in riferimento al soggetto ad esempio "th_1":

{*xgboost*} = {{‘**0-50**': valore float del best score ottenuto dal soggetto 1 sulla finestra 0-50, }
{{’25-75’}: valore float del best score ottenuto dal soggetto 1 sulla finestra 25-75... etc] }

per **svm** in riferimento al soggetto ad esempio "th_1":

{*svm*} = {{‘**0-50**': valore float del best score ottenuto dal soggetto 1 sulla finestra 0-50, }
{’25-75’}: valore float del best score ottenuto dal soggetto 1 sulla finestra 25-75... etc] 

quindi in sostanza, "**best_scores_level_4_single_th**" sarà un **dizionario annidato**, 

che conterrà come primo dizionario come chiave il nome del soggetto iterato (th_1, th_2 etc) che avrà come valore, 

altri 3 dizionari (quelli dei 3 classificatori rispetto al soggetto th_1) , ognuno che ha come chiave il nome del classificatore 

(quindi *logistic regression* *xgboost* e *svm*)

e poi

come sotto-sotto-sotto- valore di ogni sotto-sotto-dizionario del relativo classificatore, 


un altro dizionario, che ha come chiave il valore stringa di quella finestra, e 
come sotto-sotto-sotto-sotto-valore, 

il valore di best score ottenuto da quel soggetto lì, per quella finestra testata, per quel classificatore lì, ognuno dopo l'altro ...

Infatti, percorrendo tutto il file .txt, avrai altre righe in cui potrebbe comparire questa sequenza di stringhe del tipo 

"Best Score for Window {elemento di n_windows} ".. 

Quindi, alla fine, creerò un numero di dizionari pari al numero di soggetti, ossia 

th_1
th_2
th_3
th_4
th_5
th_6
th_7
th_8
th_9
th_10
th_11
th_12
th_13
th_14
th_15

dove ciascuno conterrà altri 3 dizionari 

(quelli dei classificatori testati per il relativo soggetto) seguito da

un altro dizionario, che ha come chiavi il numero di finestre per cui ho calcolato il best score per la relativa finestra, che sarà diversa per ogni finestra ovviamente 

e come valore di quest'ultimo dizionario, il valore di best score ottenuto da quel soggetto lì, per quella finestra lì, con quello specifico classificatore...

Quindi, la costruzione di questi dizionari annidati sarà del tipo:

th_1 --> dentro *logistic regression*, *xgboost*, *svm* dentro ognuno avrò questa struttura ad esempio

0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121

Ognuna, quindi, dovrà conteggiare 

i best score ottenuti da ogni singolo soggetto, 
per quello specifico classificatore,
per quella finestra di segnale EEG, 
per il livello di ricostruzione considerato,

(che è identificato dall'aver visto se la porzione finale della stringa associata al nome del file contenga la stringa "_level_4_std" o "_level_5_std, quando iteri dentro la folder path)...


<br>

Infatti, la stessa sequenza di passaggi vorrei che venisse eseguita quando si controlla che la porzione finale della stringa associata al nome del file contenga la stringa "_level_5_std" ...

quindi in quel caso creerò un altro dizionario **best_scores_level_5_single_th**, con dentro una stessa struttura ossia


th_1 (con dentro *logistic regression*, *xgboost*, *svm* )
th_2 (con dentro *logistic regression*, *xgboost*, *svm* )
th_3 (con dentro *logistic regression*, *xgboost*, *svm* )
th_4 (con dentro *logistic regression*, *xgboost*, *svm* )
th_5 (con dentro *logistic regression*, *xgboost*, *svm* )
th_6 (con dentro *logistic regression*, *xgboost*, *svm* )
th_7 (con dentro *logistic regression*, *xgboost*, *svm* )
th_8 (con dentro *logistic regression*, *xgboost*, *svm* )
th_9 (con dentro *logistic regression*, *xgboost*, *svm* )
th_10 (con dentro *logistic regression*, *xgboost*, *svm* )
th_11 (con dentro *logistic regression*, *xgboost*, *svm* )
th_12 (con dentro *logistic regression*, *xgboost*, *svm* )
th_13 (con dentro *logistic regression*, *xgboost*, *svm* )
th_14 (con dentro *logistic regression*, *xgboost*, *svm* )
th_15 (con dentro *logistic regression*, *xgboost*, *svm* )


ognuna con dentro 


0-50: 0.2681818181818182
25-75: 0.2681818181818182
50-100: 0.2681818181818182
75-125: 0.2621212121212121
100-150: 0.2621212121212121
125-175: 0.2621212121212121
150-200: 0.2621212121212121
175-225: 0.2621212121212121
200-250: 0.2681818181818182
225-275: 0.2621212121212121
250-300: 0.2621212121212121




<br>

Quindi che nel codice voglio che si prenda dal relativo file .txt del soggetto 

(per i due livelli di ricostruzione del segnale, ossia ad esempio dentro la sotto-path del folder associato ad ogni classificatore del primo soggetto 
 "/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/logistic_regression/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/xgboost/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"

"/home/stefano/Interrogait/Plots_Sliding_Estimator_MNE/svm/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_therapists_optimized_params"
 acceda dentro 

"optimized_params_th_1_level_4_std.txt" e 
"optimized_params_th_1_level_5_std.txt"

E, per ogni finestra considerata
(i.e., n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
"150-200", "175-225", "200-250", "225-275", "250-300"])

Mi appenda, nella relativa sottochiave del sotto-dizionario associato al classificatore dello specifico soggetto, il migliore best score che il soggetto ad esempio 1 ha ottenuto quella finestra lì, per quel livello di ricostruzione lì, per quel classificatore lì (accedendo come ti ho detto alle varie sotto-path dei folder dei classificatori)....

ossia per la prima che sarà 0-50
e così via per le altre...

e che la stessa cosa la deve fare per ogni soggetto (th_2, th_3 etc.)


<br>
<br>
<br>




##### **ALL SINGLE Patients (PT01-PT19) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DALLE RICOSTRUZIONI DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM)**

##### **ALL SINGLE Patients (PT01-PT19) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 DA COEFF DETAIL DALLE RICOSTRUZIONI DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM)**

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)
    

In [ ]:
import os

def process_txt_files(base_path, classifiers, n_windows):
    best_scores_level_4 = {}
    best_scores_level_5 = {}
    best_scores_level_5_detail = {}  # Nuova variabile per i coefficienti di dettaglio del 5° livello
    
    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(base_path, classifier, "EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params")
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)
                
                # Escludi i file che contengono "invalid_params", "all_pt_level_4", o "all_pt_level_5"
                if "invalid_params" in file_name or 'all_pt_level_4' in file_name or 'all_pt_level_5' in file_name:
                    continue
                
                # Determina il livello dal nome del file
                if "_level_approx_4_std" in file_name:
                    level = 'approx_4'
                elif "_level_approx_5_std" in file_name:
                    level = 'approx_5'
                elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                    level = "detail_5"
                else:
                    continue  # Salta il file se non è né livello 4 né livello 5
                
                # Verifica che il file sia per uno specifico soggetto (th_1, th_2, ..., th_15)
                subject = None
                if "pt_" in file_name:
                    try:
                        subject = file_name.split("pt_")[1].split("_")[0]  # Estrai il numero del soggetto (1-15)
                        subject = int(subject)  # Converte in intero per verificare che sia un numero valido
                        subject_key = f"pt_{subject}"  # Se tutto va bene, crea la chiave
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue  # Se c'è un errore, passa al prossimo file
                
                # Se il file è di tipo "approx_4"
                if level == 'approx_4':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_4:
                        best_scores_level_4[subject_key] = {}

                    if classifier not in best_scores_level_4[subject_key]:
                        best_scores_level_4[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_4[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break

                # Se il file è di tipo "approx_5"
                elif level == 'approx_5':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5:
                        best_scores_level_5[subject_key] = {}

                    if classifier not in best_scores_level_5[subject_key]:
                        best_scores_level_5[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break
                
                # Se il file è di tipo "detail_5"
                elif level == 'detail_5':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5_detail:
                        best_scores_level_5_detail[subject_key] = {}

                    if classifier not in best_scores_level_5_detail[subject_key]:
                        best_scores_level_5_detail[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5_detail[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break
    
    return best_scores_level_4, best_scores_level_5, best_scores_level_5_detail

# Definisci il path base e le cartelle dei classificatori
base_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE"
classifiers = ["logistic_regression", "xgboost", "svm"]

# Lista dinamica delle finestre (0-50, 25-75, ..., 250-300)
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiama la funzione per processare i file e ottenere i best scores
best_scores_level_4_single_pt_all_classifiers, best_scores_level_5_single_pt_all_classifiers, best_scores_level_5_detail_single_pt_all_classifiers = process_txt_files(base_path, classifiers, n_windows)

# Stampa i risultati
print("\033[1mbest_scores_level_4_single_pt_all_classifiers.keys()\033[0m:", best_scores_level_4_single_pt_all_classifiers.keys())
print("\n\033[1mbest_scores_level_5_single_pt_all_classifiers.keys()\033[0m:", best_scores_level_5_single_pt_all_classifiers.keys())
print("\n\033[1mbest_scores_level_5_detail_single_pt_all_classifiers.keys()\033[0m:", best_scores_level_5_detail_single_pt_all_classifiers.keys())


##### **ALL SINGLE Patients (PT01-PT19) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER EEG FILTERED 1-20 Hz DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM)**

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)

In [ ]:
import os

def process_txt_files(base_path, classifiers, n_windows):
    
    best_scores_filtered_1_20_all_classifiers_pt = {}
    
    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(base_path, classifier, "EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20")
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)
                
                # Escludi i file che contengono "invalid_params", "all_th_level_4", o "all_th_level_5"
                if "invalid_params" in file_name or 'all_th_level_4' in file_name or 'all_th_level_5' in file_name:
                    continue
                
                # Determina il livello dal nome del file
                #if "_level_approx_4_std" in file_name:
                #    level = 'approx_4'
                #elif "_level_approx_5_std" in file_name:
                #    level = 'approx_5'
                #elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                #    level = "detail_5"
                #else:
                #    continue  # Salta il file se non è né livello 4 né livello 5
                
                # Determina il livello dal nome del file
                if "filtered_1_20_std" in file_name:
                    level = 'filtered_1_20'
                else:
                    continue  # Salta il file se non è né livello 4 né livello 5
            
            
                # Verifica che il file sia per uno specifico soggetto (th_1, th_2, ..., th_15)
                subject = None
                if "pt_" in file_name:
                    try:
                        subject = file_name.split("pt_")[1].split("_")[0]  # Estrai il numero del soggetto (1-15)
                        subject = int(subject)  # Converte in intero per verificare che sia un numero valido
                        subject_key = f"pt_{subject}"  # Se tutto va bene, crea la chiave
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue  # Se c'è un errore, passa al prossimo file
                
                # Se il file è di tipo "approx_4"
                if level == 'filtered_1_20':
                    
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_filtered_1_20_all_classifiers_pt: 
                        best_scores_filtered_1_20_all_classifiers_pt[subject_key] = {}

                    if classifier not in best_scores_filtered_1_20_all_classifiers_pt[subject_key]:
                        best_scores_filtered_1_20_all_classifiers_pt[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_filtered_1_20_all_classifiers_pt[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break

               
    return best_scores_filtered_1_20_all_classifiers_pt

# Definisci il path base e le cartelle dei classificatori
base_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE"
classifiers = ["logistic_regression", "xgboost", "svm"]

# Lista dinamica delle finestre (0-50, 25-75, ..., 250-300)
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiama la funzione per processare i file e ottenere i best scores
best_scores_filtered_1_20_all_classifiers_pt = process_txt_files(base_path, classifiers, n_windows)

# Stampa i risultati
print("\033[1mbest_scores_filtered_1_20_all_classifiers_pt.keys()\033[0m:", best_scores_filtered_1_20_all_classifiers_pt.keys())


In [ ]:
best_scores_filtered_1_20_all_classifiers_pt['pt_1']['logistic_regression'].keys()

##### **ALL SINGLE Patients (PT01-PT19) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DALLE RICOSTRUZIONI DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) PER LA RELATIVA FINESTRA TESTATA -OLD VERSION** 

##### **ALL SINGLE Patients (PT01-PT19) CODE PER PLOTS BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX & LEVEL 5 DA COEFF DETAIL DELLE RICOSTRUZIONI DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) PER LA RELATIVA FINESTRA TESTATA**)

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DEL FINESTRE'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

# Definisci una mappa di colori per i classificatori
color_map = {
    'logistic_regression': 'green',
    'xgboost': 'purple',
    'svm': 'blue'
}

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

def plot_best_scores_for_subjects(best_scores_level_dict, level, save_path):
    
    pts_baseline_accuracy_highest_class_in_fold = list()
    
    # Crea la cartella principale 'patient'
    
    #main_save_path = os.path.join(save_path, 'therapist_wavelet_levels')
    main_save_path = os.path.join(save_path, 'wavelet_levels', 'patients')
    os.makedirs(main_save_path, exist_ok=True)
    
    
    for subject, subj_classifier in best_scores_level_dict.items():
        
        # Crea la directory per il soggetto
        subject_dir = os.path.join(main_save_path, f'single_{subject}')
        os.makedirs(subject_dir, exist_ok=True)

        for classifier, win_scores in subj_classifier.items():
            
            # Estrai le chiavi delle finestre e i punteggi per il classificatore corrente
            windows = list(win_scores.keys())
            scores_list = [win_scores[window] for window in windows]
            
        # Controllo delle labels per il soggetto attuale
        if subject in new_subject_level_concatenations_pt:
            
            # Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_pt[subject]['labels']
            unique_values, labels_counts = np.unique(labels, return_counts=True)
            num_folds = 5 
            total_labels = np.sum(labels_counts)
            elements_per_fold = total_labels / 5
            rounded_elements_per_fold = math.floor(elements_per_fold)
            class_percentage = labels_counts / total_labels * 100
            highest_class_percentage = max(class_percentage)
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
            pts_baseline_accuracy_highest_class_in_fold.append(baseline_accuracy_highest_class_in_fold)
            
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

        # Inizio del Plot
        plt.figure(figsize=(10, 8))
        plt.subplots_adjust(bottom = 0.25)  # Lascia spazio per la legenda
        
        # Crea etichette per le finestre 
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        # Imposta le etichette principali
        plt.xticks(tick_positions, window_labels)
        
        # Aggiungi i punteggi dei classificatori per ogni finestra
        for classifier in ['logistic_regression', 'xgboost', 'svm']:
            
            if subject in best_scores_level_dict:
                classifier_scores_list = []
                
                for window in windows:
                    score = best_scores_level_dict[subject][classifier].get(window, 0)
                    classifier_scores_list.append(score)
                
                #plt.scatter(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color=color_map[classifier])
                plt.plot(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color=color_map[classifier])
                
        # Configura la legenda per i punteggi dei soggetti
        handles, labels = plt.gca().get_legend_handles_labels()  # Ottieni i handle e le etichette esistenti
        
        custom_lines = [plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10) for classifier in best_scores_level_dict[subject].keys()]
        
        for classifier in best_scores_level_dict[subject].keys():
            
            if classifier in color_map:
                custom_lines.append(plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10))
                
        plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subj {subject}')

        plt.xlabel('Windows (50 samples)', fontweight='bold')
        plt.ylabel('Best Accuracy Score', fontweight='bold')

        # Titolo a seconda del livello
        
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        # Titolo a seconda del livello
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for  Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for  Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for  Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for  Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        
        if level == 'approx_4':
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ + δ range: 0-7.812 Hz)')
            level_str = 'theta'
        elif level == 'approx_5':
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)')
            level_str = 'delta'
        elif level == 'detail_5':  # Gestione del livello di dettaglio
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)')
            level_str = 'theta_strict'
            

        plt.grid(True)
        
        custom_lines = [
            plt.Line2D([0], [0], color='black', linestyle='--', label='End of Prestimulus (50th sample)'),
            plt.Line2D([0], [0], color='red', linestyle='--', label=f'Chance Level for Subj {subject}')
        ]
        
        #plt.legend(['logistic_regression', 'xgboost', 'svm', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
        plt.legend(['logistic regression performance for $i^{{th}}$ Window', 'xgboost performance for $i^{{th}}$ Window', 'svm performance for $i^{{th}}$ Window', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
        
        filename = f'best_scores_subject_{subject}_{level_str}_all_classifiers_window_domain.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.tight_layout()
        #plt.show()
        
        plt.savefig(save_file_path, bbox_inches='tight')
        print(f'\nPlot salvato in: \033[1m{save_file_path}\033[0m\n')
        plt.close()

    return pts_baseline_accuracy_highest_class_in_fold

                
# Esempio di utilizzo

save_path_level_4 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'
save_path_level_5 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'
save_path_level_5_detail = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'


# Esegui la funzione per ogni livello
all_pts_baseline_accuracy_highest_class_in_fold_level_4 = plot_best_scores_for_subjects(best_scores_level_4_single_pt_all_classifiers, 'approx_4', save_path_level_4)
all_pts_baseline_accuracy_highest_class_in_fold_level_5 = plot_best_scores_for_subjects(best_scores_level_5_single_pt_all_classifiers, 'approx_5', save_path_level_5)
all_pts_baseline_accuracy_highest_class_in_fold_level_5_detail = plot_best_scores_for_subjects(best_scores_level_5_detail_single_pt_all_classifiers, 'detail_5', save_path_level_5_detail)


In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DEL TEMPO'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

# Definisci una mappa di colori per i classificatori
color_map = {
    'logistic_regression': 'green',
    'xgboost': 'purple',
    'svm': 'blue'
}

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

def plot_best_scores_for_subjects(best_scores_level_dict, level, save_path):
    
    pts_baseline_accuracy_highest_class_in_fold = list()
    
    # Crea la cartella principale 'patient'
    
    #main_save_path = os.path.join(save_path, 'therapist_wavelet_levels')
    main_save_path = os.path.join(save_path, 'wavelet_levels', 'patients')
    os.makedirs(main_save_path, exist_ok=True)
    
    
    for subject, subj_classifier in best_scores_level_dict.items():
        
        # Crea la directory per il soggetto
        subject_dir = os.path.join(main_save_path, f'single_{subject}')
        os.makedirs(subject_dir, exist_ok=True)

        for classifier, win_scores in subj_classifier.items():
            
            # Estrai le chiavi delle finestre e i punteggi per il classificatore corrente
            windows = list(win_scores.keys())
            scores_list = [win_scores[window] for window in windows]
            
        # Controllo delle labels per il soggetto attuale
        if subject in new_subject_level_concatenations_pt:
            
            # Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_pt[subject]['labels']
            unique_values, labels_counts = np.unique(labels, return_counts=True)
            num_folds = 5 
            total_labels = np.sum(labels_counts)
            elements_per_fold = total_labels / 5
            rounded_elements_per_fold = math.floor(elements_per_fold)
            class_percentage = labels_counts / total_labels * 100
            highest_class_percentage = max(class_percentage)
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            
            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
            pts_baseline_accuracy_highest_class_in_fold.append(baseline_accuracy_highest_class_in_fold)
            
        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

        # Inizio del Plot
        plt.figure(figsize=(10, 8))
        plt.subplots_adjust(bottom = 0.25)  # Lascia spazio per la legenda
        
        # Crea etichette per le finestre 
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        # Imposta le etichette principali
        #plt.xticks(tick_positions, window_labels)
        
        '''PER RAPPRESENTAZIONE NEL DOMINIO DEL TEMPO'''
        plt.xticks(window_mid_points_in_ms, [f'{int(pos)} ms' for pos in window_mid_points_in_ms])
        
        # Aggiungi i punteggi dei classificatori per ogni finestra
        for classifier in ['logistic_regression', 'xgboost', 'svm']:
            
            if subject in best_scores_level_dict:
                classifier_scores_list = []
                
                for window in windows:
                    score = best_scores_level_dict[subject][classifier].get(window, 0)
                    classifier_scores_list.append(score)
                
                #plt.scatter(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color=color_map[classifier])
                plt.plot(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color=color_map[classifier])
                
        # Configura la legenda per i punteggi dei soggetti
        handles, labels = plt.gca().get_legend_handles_labels()  # Ottieni i handle e le etichette esistenti
        
        custom_lines = [plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10) for classifier in best_scores_level_dict[subject].keys()]
        
        for classifier in best_scores_level_dict[subject].keys():
            
            if classifier in color_map:
                custom_lines.append(plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10))
                
        '''PER RAPPRESENTAZIONE NEL DOMINIO DEL TEMPO'''
        # Linea verticale tratteggiata per indicare la fine del prestimolo a 200 ms
        plt.axvline(x=0, color='black', linestyle='--', label='End of Prestimulus (0 ms)')
    
        plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level for Subj {subject}')

        plt.xlabel('Time', fontweight='bold')
        plt.ylabel('Best Accuracy Score', fontweight='bold')

        # Titolo a seconda del livello
        
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        # Titolo a seconda del livello
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for  Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for  Win $i_{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        #if level == 'approx_4':
        #    plt.title(f'Best Accuracy Score for Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4(Θ+δ range 0-7.8125 Hz)')
        #    level_str = 'theta'
        #elif level == 'approx_5':
        #    plt.title(f'Best Accuracy Score for  Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5(δ-range 0-3.9 Hz)')
        #    level_str = 'delta'
        #elif level == 'detail_5':  # Gestione del livello di dettaglio
        #    plt.title(f'Best Accuracy Score for  Win $i_{{i}}^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range 3.9-7.8125 Hz)')
        #    level_str = 'theta_strict'
        
        
        if level == 'approx_4':
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 4 (Θ + δ range: 0-7.812 Hz)')
            level_str = 'theta'
        elif level == 'approx_5':
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Approx 5 (δ-range: 0-3.9 Hz)')
            level_str = 'delta'
        elif level == 'detail_5':  # Gestione del livello di dettaglio
            plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - Coeff Detail 5 (Θ-range: 3.9-7.812 Hz)')
            level_str = 'theta_strict'
            

        plt.grid(True)
        
        custom_lines = [
            plt.Line2D([0], [0], color='black', linestyle='--', label='End of Prestimulus (50th sample)'),
            plt.Line2D([0], [0], color='red', linestyle='--', label=f'Chance Level for Subj {subject}')
        ]
        
        #plt.legend(['logistic_regression', 'xgboost', 'svm', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
        plt.legend(['logistic regression performance for $i^{{th}}$ Window', 'xgboost performance for $i^{{th}}$ Window', 'svm performance for $i^{{th}}$ Window', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
        
        filename = f'best_scores_subject_{subject}_{level_str}_all_classifiers_time_domain.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.tight_layout()
        #plt.show()
        
        plt.savefig(save_file_path, bbox_inches='tight')
        print(f'\nPlot salvato in: \033[1m{save_file_path}\033[0m\n')
        plt.close()

    return pts_baseline_accuracy_highest_class_in_fold

                
# Esempio di utilizzo

save_path_level_4 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'
save_path_level_5 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'
save_path_level_5_detail = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap'


# Esegui la funzione per ogni livello
all_pts_baseline_accuracy_highest_class_in_fold_level_4 = plot_best_scores_for_subjects(best_scores_level_4_single_pt_all_classifiers, 'approx_4', save_path_level_4)
all_pts_baseline_accuracy_highest_class_in_fold_level_5 = plot_best_scores_for_subjects(best_scores_level_5_single_pt_all_classifiers, 'approx_5', save_path_level_5)
all_pts_baseline_accuracy_highest_class_in_fold_level_5_detail = plot_best_scores_for_subjects(best_scores_level_5_detail_single_pt_all_classifiers, 'detail_5', save_path_level_5_detail)


In [ ]:
!pwd

In [ ]:
print(all_pts_baseline_accuracy_highest_class_in_fold_level_4)
print()
print(all_pts_baseline_accuracy_highest_class_in_fold_level_5)
print()
print(all_pts_baseline_accuracy_highest_class_in_fold_level_5_detail)


In [ ]:
# Salvare l'intero dizionario annidato con pickle

'SALVATAGGIO PERFORMANCE PAZIENTI SU TUTTI CLASSIFICATORI'

import pickle

with open('best_scores_level_4_single_pt_all_classifiers.pkl', 'wb') as f:
    pickle.dump(best_scores_level_4_single_pt_all_classifiers, f)

with open('best_scores_level_5_single_pt_all_classifiers.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_single_pt_all_classifiers, f)
    
with open('best_scores_level_5_detail_single_pt_all_classifiers.pkl', 'wb') as f:
    pickle.dump(best_scores_level_5_detail_single_pt_all_classifiers, f)
        
        
'SALVATAGGIO BASELINE ACCURACY LEVEL PAZIENTI SU TUTTI CLASSIFICATORI PER LIVELLO θ + δ, δ e θ'

with open('new_baseline_accuracy_all_subjects_pt.pkl', 'wb') as f:
    pickle.dump(all_pts_baseline_accuracy_highest_class_in_fold_level_4, f)    

In [ ]:
!pwd

In [ ]:
with open('new_baseline_accuracy_all_subjects_pt.pkl', 'wb') as f:
    pickle.dump(all_pts_baseline_accuracy_highest_class_in_fold_level_4, f)

##### **ALL SINGLE Patients (PT01-PT19) CODE PER PLOTS BEST PERFORMANCES SALVATE PER EEG FILTERED 1-20 Hz DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) PER LA RELATIVA FINESTRA TESTATA** 

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DEL FINESTRE'''

#PLOTS 

# UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE! 
#RESULTS DI OGNI CLASSIFICATORE DELLA STESSA FINESTRA PER LO STESSO SINGOLO SOGGETTO!

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni


# Definisci una mappa di colori per i classificatori

#verde scuro 
#rosa fuscia
#azzurro acceso
'''
# Plot con colori personalizzati
plt.plot(x, y1, color='#006400', label='Verde Scuro')
plt.plot(x, y2, color='#FF00FF', label='Rosa Fucsia')
plt.plot(x, y3, color='#00BFFF', label='Azzurro Acceso')
'''


color_map = {
    'logistic_regression': '#006400',
    'xgboost': '#FF00FF',
    'svm': '#00BFFF',
}

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

def plot_best_scores_for_subjects(best_scores_dict, save_path):
    
    # ths_baseline_accuracy_highest_class_in_fold_1_20:
    
    # conterrà una lista di accuracies di baseline per ogni soggetto.
    # Poiché i dati del soggetto rimangono gli stessi per i diversi classificatori,
    # l'accuratezza di baseline calcolata sarà la stessa per tutti e tre i classificatori.
    # Pertanto, si avrà lo stesso valore di baseline_accuracy_highest_class_in_fold per il soggetto,
    # indipendentemente dal classificatore utilizzato
    
    pts_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers = list()
    
    for subject, subj_classifier in best_scores_dict.items():
        
        # Crea la directory per il soggetto
        subject_dir = os.path.join(save_path, f'single_{subject}_filtered_1_20')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        '''OLD VERSION'''
        # Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        #windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #scores_list = [scores[window] for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        # Itera su ciascun classificatore
        for classifier, win_scores in subj_classifier.items():
            
            # Estrai le chiavi delle finestre e i punteggi per il classificatore corrente
            windows = list(win_scores.keys())
            #print(f"\033[1mClassifier: \t\033[1m{classifier}\033[0m")
            #print(f"\033[1mN ° Windows\033[0m: {windows}")

            scores_list = [win_scores[window] for window in windows]
            #print(f"\033[1mBest scores of {classifier} for {subject}\033[0m: {scores_list}\n\n")
            
        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th_1_20:
        
        if subject in new_subject_level_concatenations_pt_1_20:
        
            # Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_pt_1_20[subject]['labels']
            unique_values, labels_counts = np.unique(labels, return_counts=True)
            num_folds = 5 
            print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")
            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")
            elements_per_fold = total_labels / 5
            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            class_percentage = labels_counts / total_labels * 100
            print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
            print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")
            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            pts_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers.append(baseline_accuracy_highest_class_in_fold)

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

        # Inizio del Plot
        plt.figure(figsize=(10, 8))
        plt.subplots_adjust(bottom = 0.25)  # Lascia spazio per la legenda
        
        # Crea etichette per le finestre 
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        # Imposta le etichette principali
        plt.xticks(tick_positions, window_labels)
        
        # Aggiungi i punteggi dei classificatori per ogni finestra
        for classifier in ['logistic_regression', 'xgboost', 'svm']:
            
            #itero sul grande dizionario annidato che do come argomento alla funzione
            #(i.e., best_scores_1_20_single_th_all_classifiers)
            
            if subject in best_scores_dict:
                classifier_scores_list = []
                
                for window in windows:
                    score = best_scores_dict[subject][classifier].get(window, 0)
                    
                    #classifier_scores_list sarà di lunghezza 3, 
                    #che conterrà i punteggi di best score di ogni classificatore 
                    #per la stessa finestra, 
                    #per l'i-esimo soggetto iterato
                    
                    classifier_scores_list.append(score)
                
                #plt.scatter(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color = color_map[classifier])
                plt.plot(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color = color_map[classifier])
        
        # Configura la legenda per i punteggi dei soggetti
        handles, labels = plt.gca().get_legend_handles_labels()  # Ottieni i handle e le etichette esistenti
        
        # Crea una legenda personalizzata per i classificatori
        custom_lines = [plt.Line2D([0], [0], marker='o', color='w', markerfacecolor = color_map[classifier], markersize=10) for classifier in best_scores_dict[subject].keys()]
        
        for classifier in best_scores_dict[subject].keys():
            
            if classifier in color_map:  # Controlla se il classificatore è presente nel color_map
                custom_lines.append(plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10))
                
        # Legenda per i classificatori sotto l'asse X
        #plt.legend(handles, labels, loc='lower center', bbox_to_anchor=(0.5, -0.15), title='Classifiers', ncol=3)

        # Linea verticale tratteggiata nera per il 50° campione (prestimolo)
        plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')

        # Asterisco per indicare il chance level
        plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label = f'Chance Level for Subj {subject}')

        plt.xlabel('Windows (50 samples)', fontweight='bold')
        plt.ylabel('Best Accuracy Score', fontweight='bold')

        # Titolo per i plots
        #plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - EEG filter 1-20 Hz')    
        
        
        plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG preprocessed 1-20Hz')
        level_str = 'filtered_1_20'
            
        #plt.legend(loc = 'upper center', bbox_to_anchor=(0.5, -0.15), ncol=4)
        plt.grid(True)
        
        # Legenda per pre-stimulus e chance level
        custom_lines = [
            plt.Line2D([0], [0], color='black', linestyle='--', label='End of Prestimulus (50th sample)'),
            plt.Line2D([0], [0], color='red', linestyle='--', label=f'Chance Level for Subj {subject}')
        ]
        #plt.legend(handles=custom_lines, loc='lower center', bbox_to_anchor=(0.5, -0.1), title='Prestimulus & Chance Level', ncol=2)
        #plt.legend(handles=custom_lines, loc='best', title = f'Prestimulus Period & Chance Level Accuracy for {subject}', ncol = 3)
        
        #plt.legend(handles=custom_lines, loc='lower center', bbox_to_anchor=(0.5, -0.1), ncol=2)
        
        plt.legend(['logistic_regression', 'xgboost', 'svm', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
    
        # Salva il plot sul path specifico
        filename = f'best_scores_subject_{subject}_{level_str}_window_domain.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.tight_layout()
        #plt.show()
        plt.savefig(save_file_path, bbox_inches='tight')
        print(f'\nPlot salvato in: \033[1m{save_file_path}\033[0m\n')
        plt.close()

    return pts_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers

                
# Esempio di utilizzo
save_path_pt_1_20 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/original_filtered_1_20/patient_1_20'

# Crea la cartella se non esiste
os.makedirs(save_path_pt_1_20, exist_ok=True)

# Esegui la funzione per ogni livello
pts_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers = plot_best_scores_for_subjects(best_scores_filtered_1_20_all_classifiers_pt, save_path_pt_1_20)


In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW VERSION - DOMINIO DEL TEMPO'''

#PLOTS 

# UFFICIALE: ASSE X NEL DOMINIO DELLE FINESTRE! 
#RESULTS DI OGNI CLASSIFICATORE DELLA STESSA FINESTRA PER LO STESSO SINGOLO SOGGETTO!

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni


# Definisci una mappa di colori per i classificatori

#verde scuro 
#rosa fuscia
#azzurro acceso
'''
# Plot con colori personalizzati
plt.plot(x, y1, color='#006400', label='Verde Scuro')
plt.plot(x, y2, color='#FF00FF', label='Rosa Fucsia')
plt.plot(x, y3, color='#00BFFF', label='Azzurro Acceso')
'''


color_map = {
    'logistic_regression': '#006400',
    'xgboost': '#FF00FF',
    'svm': '#00BFFF',
}

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

def plot_best_scores_for_subjects(best_scores_dict, save_path):
    
    # ths_baseline_accuracy_highest_class_in_fold_1_20:
    
    # conterrà una lista di accuracies di baseline per ogni soggetto.
    # Poiché i dati del soggetto rimangono gli stessi per i diversi classificatori,
    # l'accuratezza di baseline calcolata sarà la stessa per tutti e tre i classificatori.
    # Pertanto, si avrà lo stesso valore di baseline_accuracy_highest_class_in_fold per il soggetto,
    # indipendentemente dal classificatore utilizzato
    
    pts_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers = list()
    
    for subject, subj_classifier in best_scores_dict.items():
        
        # Crea la directory per il soggetto
        subject_dir = os.path.join(save_path, f'single_{subject}_filtered_1_20')
        os.makedirs(subject_dir, exist_ok=True)

        # Estrai le chiavi delle finestre e i punteggi per il soggetto corrente
        #print(f"\n\n\033[1mTherapist: {subject}\033[0m\n")
        
        '''OLD VERSION'''
        # Creo una lista delle stringhe associate alle chiavi di secondo ordine delle finestre considerate
        #windows = list(scores.keys())
        #print(f"N ° Windows: {windows}")
        #scores_list = [scores[window] for window in windows]
        #print(f"Best scores of {subject}: {scores_list}\n\n")
        
        # Itera su ciascun classificatore
        for classifier, win_scores in subj_classifier.items():
            
            # Estrai le chiavi delle finestre e i punteggi per il classificatore corrente
            windows = list(win_scores.keys())
            #print(f"\033[1mClassifier: \t\033[1m{classifier}\033[0m")
            #print(f"\033[1mN ° Windows\033[0m: {windows}")

            scores_list = [win_scores[window] for window in windows]
            #print(f"\033[1mBest scores of {classifier} for {subject}\033[0m: {scores_list}\n\n")
            
        
        # Controllo delle labels per il soggetto attuale
        #if subject in subject_level_concatenations_th_1_20:
        
        if subject in new_subject_level_concatenations_pt_1_20:
        
            # Prendo il vettore delle labels di quel soggetto specifico
            labels = new_subject_level_concatenations_pt_1_20[subject]['labels']
            unique_values, labels_counts = np.unique(labels, return_counts=True)
            num_folds = 5 
            print(f"For \033[1m{subject}\033[0m the labels vector and counts are \n{unique_values}, \n{labels_counts}")
            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1m{subject}\033[0m: {np.sum(labels_counts)}")
            elements_per_fold = total_labels / 5
            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\n\033[1mElements per Fold (rounded by defect)\033[0m for \033[1m{subject}\033[0m: {rounded_elements_per_fold}")
            class_percentage = labels_counts / total_labels * 100
            print(f"\n\033[1mClass Percentage\033[0m for \033[1m{subject}\033[0m: {class_percentage}")
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{subject}\033[0m is: {highest_class_percentage}")
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
            print(f"\n\033[1mN° Samples per Fold for Highest Class for \033[1m{subject}\033[0m is: {rounded_elements_per_fold} * ({highest_class_percentage}/{'100'}) = {samples_for_highest_class}")
            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            print(f"\n\033[1mN° Exceeded Samples for Highest Class in Fold for \033[1m{subject}\033[0m is: {samples_for_highest_class} ~= {exceeded_round_samples_for_highest_class}")

            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{subject}\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            pts_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers.append(baseline_accuracy_highest_class_in_fold)

        # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
        window_starts_samples = []
        window_ends_samples = []
        window_mid_points_samples = []

        # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
        start_sample = 0
        while start_sample + window_size_samples <= n_samples:
            end_sample = start_sample + window_size_samples
            window_starts_samples.append(start_sample)
            window_ends_samples.append(end_sample)
            window_mid_points_samples.append(start_sample + window_size_samples // 2)
            start_sample += stride_samples

        # Conversione dei punti in millisecondi
        window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

        # Inizio del Plot
        plt.figure(figsize=(10, 8))
        plt.subplots_adjust(bottom = 0.25)  # Lascia spazio per la legenda
        
        # Crea etichette per le finestre 
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms
        
        '''PER RAPPRESENTAZIONE NEL DOMINIO FINESTRE'''
        # Imposta le etichette principali
        #plt.xticks(tick_positions, window_labels)
        
        '''PER RAPPRESENTAZIONE NEL DOMINIO DEL TEMPO'''
        plt.xticks(window_mid_points_in_ms, [f'{int(pos)} ms' for pos in window_mid_points_in_ms])
        
        # Aggiungi i punteggi dei classificatori per ogni finestra
        for classifier in ['logistic_regression', 'xgboost', 'svm']:
            
            #itero sul grande dizionario annidato che do come argomento alla funzione
            #(i.e., best_scores_1_20_single_th_all_classifiers)
            
            if subject in best_scores_dict:
                classifier_scores_list = []
                
                for window in windows:
                    score = best_scores_dict[subject][classifier].get(window, 0)
                    
                    #classifier_scores_list sarà di lunghezza 3, 
                    #che conterrà i punteggi di best score di ogni classificatore 
                    #per la stessa finestra, 
                    #per l'i-esimo soggetto iterato
                    
                    classifier_scores_list.append(score)
                
                #plt.scatter(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color = color_map[classifier])
                plt.plot(window_mid_points_in_ms, classifier_scores_list, label=f'{classifier} Scores', color = color_map[classifier])
        
        # Configura la legenda per i punteggi dei soggetti
        handles, labels = plt.gca().get_legend_handles_labels()  # Ottieni i handle e le etichette esistenti
        
        # Crea una legenda personalizzata per i classificatori
        custom_lines = [plt.Line2D([0], [0], marker='o', color='w', markerfacecolor = color_map[classifier], markersize=10) for classifier in best_scores_dict[subject].keys()]
        
        for classifier in best_scores_dict[subject].keys():
            
            if classifier in color_map:  # Controlla se il classificatore è presente nel color_map
                custom_lines.append(plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color_map[classifier], markersize=10))
                
        # Legenda per i classificatori sotto l'asse X
        #plt.legend(handles, labels, loc='lower center', bbox_to_anchor=(0.5, -0.15), title='Classifiers', ncol=3)
        
        '''PER RAPPRESENTAZIONE NEL DOMINIO FINESTRE'''
        # Linea verticale tratteggiata nera per il 50° campione (prestimolo)
        #plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        
        '''PER RAPPRESENTAZIONE NEL DOMINIO DEL TEMPO'''
        # Linea verticale tratteggiata per indicare la fine del prestimolo a 200 ms
        plt.axvline(x=0, color='black', linestyle='--', label='End of Prestimulus (0 ms)')        
        
        # Asterisco per indicare il chance level
        plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label = f'Chance Level for Subj {subject}')

        plt.xlabel('Time', fontweight='bold')
        plt.ylabel('Best Accuracy Score', fontweight='bold')

        # Titolo per i plots
        #plt.title(f'Best Accuracy Score for W-th Window (50 time points, 25 stride) - Subject {subject} - EEG filter 1-20 Hz')    
        
        
        plt.title(f'Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Subject {subject} - EEG preprocessed 1-20Hz')
        level_str = 'filtered_1_20'
            
        #plt.legend(loc = 'upper center', bbox_to_anchor=(0.5, -0.15), ncol=4)
        plt.grid(True)
        
        # Legenda per pre-stimulus e chance level
        custom_lines = [
            plt.Line2D([0], [0], color='black', linestyle='--', label='End of Prestimulus (50th sample)'),
            plt.Line2D([0], [0], color='red', linestyle='--', label=f'Chance Level for Subj {subject}')
        ]
        #plt.legend(handles=custom_lines, loc='lower center', bbox_to_anchor=(0.5, -0.1), title='Prestimulus & Chance Level', ncol=2)
        #plt.legend(handles=custom_lines, loc='best', title = f'Prestimulus Period & Chance Level Accuracy for {subject}', ncol = 3)
        
        #plt.legend(handles=custom_lines, loc='lower center', bbox_to_anchor=(0.5, -0.1), ncol=2)
        
        plt.legend(['logistic_regression', 'xgboost', 'svm', 'Prestimulus Period (50 samples)', 'Baseline Accuracy Level'])
    
        # Salva il plot sul path specifico
        filename = f'best_scores_subject_{subject}_{level_str}_time_domain.png'
        save_file_path = os.path.join(subject_dir, filename)
        plt.tight_layout()
        #plt.show()
        plt.savefig(save_file_path, bbox_inches='tight')
        print(f'\nPlot salvato in: \033[1m{save_file_path}\033[0m\n')
        plt.close()

    return pts_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers

                
# Esempio di utilizzo
save_path_pt_1_20 = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/original_filtered_1_20/patient_1_20'

# Crea la cartella se non esiste
os.makedirs(save_path_pt_1_20, exist_ok=True)

# Esegui la funzione per ogni livello
pts_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers = plot_best_scores_for_subjects(best_scores_filtered_1_20_all_classifiers_pt, save_path_pt_1_20)


In [ ]:
print(pts_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers)

In [ ]:
# Salvare l'intero dizionario annidato con pickle

'SALVATAGGIO PERFORMANCE TERAPISTI SU TUTTI CLASSIFICATORI PER EEG 1-20 Hz'

import pickle

with open('best_scores_filtered_1_20_all_classifiers_pt.pkl', 'wb') as f:
    pickle.dump(best_scores_filtered_1_20_all_classifiers_pt, f)

    
'SALVATAGGIO BASELINE ACCURACY LEVEL TERAPISTI SU TUTTI CLASSIFICATORI PER EEG 1-20 Hz'

with open('new_baseline_accuracy_all_subjects_pt_1_20.pkl', 'wb') as f:
    pickle.dump(pts_baseline_accuracy_highest_class_in_fold_1_20_all_classifiers, f)


#### **All Patients (PT01-PT20)**

### Plots of **Grand Average Mean** of Best Single Subject's Accuracy Score Performances 

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **ALL SINGLE Patients (PT01-PT19) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **NEW VERSION**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
import os

familiar_path = "New_Plots_Sliding_Estimator_MNE"

def process_txt_files(base_path, classifiers, n_windows):
    best_scores_level_4 = {}
    best_scores_level_5 = {}
    best_scores_level_5_detail = {}  # Nuova variabile per i coefficienti di dettaglio del 5° livello
    
    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(base_path, classifier, "EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params")
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)
                
                # Escludi i file che contengono "invalid_params", "all_th_level_4", o "all_th_level_5"
                if "invalid_params" in file_name or 'all_pt_level_4' in file_name or 'all_pt_level_5' in file_name:
                    continue
                
                # Determina il livello dal nome del file
                if "_level_approx_4_std" in file_name:
                    level = 'approx_4'
                elif "_level_approx_5_std" in file_name:
                    level = 'approx_5'
                elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                    level = "detail_5"
                else:
                    continue  # Salta il file se non è né livello 4 né livello 5
                
                # Verifica che il file sia per uno specifico soggetto (th_1, th_2, ..., th_15)
                subject = None
                if "pt_" in file_name:
                    try:
                        subject = file_name.split("pt_")[1].split("_")[0]  # Estrai il numero del soggetto (1-15)
                        subject = int(subject)  # Converte in intero per verificare che sia un numero valido
                        subject_key = f"pt_{subject}"  # Se tutto va bene, crea la chiave
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue  # Se c'è un errore, passa al prossimo file
                
                # Se il file è di tipo "approx_4"
                if level == 'approx_4':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_4:
                        best_scores_level_4[subject_key] = {}

                    if classifier not in best_scores_level_4[subject_key]:
                        best_scores_level_4[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_4[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break

                # Se il file è di tipo "approx_5"
                elif level == 'approx_5':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5:
                        best_scores_level_5[subject_key] = {}

                    if classifier not in best_scores_level_5[subject_key]:
                        best_scores_level_5[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break
                
                # Se il file è di tipo "detail_5"
                elif level == 'detail_5':
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5_detail:
                        best_scores_level_5_detail[subject_key] = {}

                    if classifier not in best_scores_level_5_detail[subject_key]:
                        best_scores_level_5_detail[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5_detail[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break
    
    return best_scores_level_4, best_scores_level_5, best_scores_level_5_detail

# Definisci il path base e le cartelle dei classificatori
base_path = f"/home/stefano/Interrogait/{familiar_path}"
classifiers = ["logistic_regression", "xgboost", "svm"]

# Lista dinamica delle finestre (0-50, 25-75, ..., 250-300)
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiama la funzione per processare i file e ottenere i best scores
best_scores_level_4_single_pt_all_classifiers, best_scores_level_5_single_pt_all_classifiers, best_scores_level_5_detail_single_pt_all_classifiers = process_txt_files(base_path, classifiers, n_windows)

# Stampa i risultati
print("\033[1mbest_scores_level_4_single_pt_all_classifiers.keys()\033[0m:", best_scores_level_4_single_pt_all_classifiers.keys())
print("\n\033[1mbest_scores_level_5_single_pt_all_classifiers.keys()\033[0m:", best_scores_level_5_single_pt_all_classifiers.keys())
print("\n\033[1mbest_scores_level_5_detail_single_pt_all_classifiers.keys()\033[0m:", best_scores_level_5_detail_single_pt_all_classifiers.keys())


In [ ]:
print(best_scores_level_4_single_pt_all_classifiers['pt_1'].keys())
print(best_scores_level_4_single_pt_all_classifiers['pt_1']['svm'].keys())
print(best_scores_level_4_single_pt_all_classifiers['pt_1']['svm']['0-50'])

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA PER OGNI CLASSIFIER - NEW VERSION


Spiegazione delle modifiche

- Parametro classifier nella funzione: La funzione calculate_mean_and_confidence_interval ora 
prende un parametro aggiuntivo classifier, in modo che possa calcolare le statistiche 
per un classificatore specifico all'interno della struttura best_scores.

- Raccolta dei punteggi: All'interno della funzione, per ogni finestra (window), 
raccogli i punteggi di tutti i soggetti per il classificatore specificato.

- Dizionari annidati: statistics_level_4, statistics_level_5 e statistics_level_5_detail sono ora
dizionari annidati, dove ogni classificatore ha il proprio dizionario di risultati per le varie finestre temporali.


Ecco un esempio di come apparirebbe statistics_level_4:

statistics_level_4 = {
    "logistic_regression": {
        "0-50": {
            "mean": 0.78,
            "ci_lower": 0.75,
            "ci_upper": 0.81
        },
        "25-75": {
            "mean": 0.82,
            "ci_lower": 0.79,
            "ci_upper": 0.85
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.76,
            "ci_lower": 0.72,
            "ci_upper": 0.80
        }
    },
    "xgboost": {
        "0-50": {
            "mean": 0.80,
            "ci_lower": 0.77,
            "ci_upper": 0.83
        },
        "25-75": {
            "mean": 0.84,
            "ci_lower": 0.81,
            "ci_upper": 0.87
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.79,
            "ci_lower": 0.75,
            "ci_upper": 0.83
        }
    },
    "svm": {
        "0-50": {
            "mean": 0.77,
            "ci_lower": 0.74,
            "ci_upper": 0.80
        },
        "25-75": {
            "mean": 0.81,
            "ci_lower": 0.78,
            "ci_upper": 0.84
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.75,
            "ci_lower": 0.71,
            "ci_upper": 0.79
        }
    }
}
'''

import numpy as np
import scipy.stats as stats

n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
             "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, classifier, windows, confidence_level=0.95):
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario per un classificatore specifico.
    """
    results = {}

    for window in windows:
        
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti per il classificatore specificato
        scores = [subject_scores[classifier][window] 
                  for subject_scores in best_scores.values() 
                  if window in subject_scores[classifier]]
        
        '''???CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW???''' 
        #print(f"Scores for \033[1mwindow {window}\033[0m: {scores}\n")

        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per ciascun classificatore nei best scores di livello 4
statistics_level_4 = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_4_single_pt_all_classifiers, classifier, n_windows)
    for classifier in ["logistic_regression", "xgboost", "svm"]
}

# Esegui la funzione per ciascun classificatore nei best scores di livello 5
statistics_level_5 = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_5_single_pt_all_classifiers, classifier, n_windows)
    for classifier in ["logistic_regression", "xgboost", "svm"]
}

# Esegui la funzione per ciascun classificatore nei best scores di dettaglio di livello 5
statistics_level_5_detail = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_5_detail_single_pt_all_classifiers, classifier, n_windows)
    for classifier in ["logistic_regression", "xgboost", "svm"]
}

# Funzione per stampare i risultati con i classificatori in grassetto
def print_bold_statistics(statistics):
    for classifier in statistics:
        print(f"\033[1m{classifier}\033[0m")  # Stampa il nome del classificatore in grassetto
        for window, stats in statistics[classifier].items():
            print(f"  {window}: Mean = {stats['mean']:.2f}, CI Lower = {stats['ci_lower']:.2f}, CI Upper = {stats['ci_upper']:.2f}")

# Stampa i risultati per ciascun livello
print("Risultati per il livello 4:\n")
print_bold_statistics(statistics_level_4)

print("\n\nRisultati per il livello 5:\n")
print_bold_statistics(statistics_level_5)

print("\n\nRisultati per il dettaglio livello 5:\n")
print_bold_statistics(statistics_level_5_detail)

In [ ]:
'''???CHECK PER VERIFICARE CHE PRENDA I RELATIVI BEST SCORE DI OGNI SOGGETTO SULLA STESSA WINDOW???''' 
#print(best_scores_level_4_single_th_lr['th_1']['0-50'])
#print(best_scores_level_4_single_th_lr['th_2']['0-50'])
#print(best_scores_level_4_single_th_lr['th_3']['0-50'])
#print()
#print(best_scores_level_4_single_th_lr['th_1']['25-75'])
#print(best_scores_level_4_single_th_lr['th_2']['25-75'])
#print(best_scores_level_4_single_th_lr['th_3']['25-75'])

In [ ]:
type(statistics_level_4)

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle


path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_all_pt_concat_reconstructions.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_pt['pt_1'].keys()

In [ ]:
new_all_pt_concat_reconstructions.keys()

In [ ]:
print(new_all_pt_concat_reconstructions['all_pt_fourth_labels'].shape)
print(new_all_pt_concat_reconstructions['all_pt_fifth_labels'].shape)
print(new_all_pt_concat_reconstructions['all_pt_fifth_detail_labels'].shape)
print()
print(np.unique(new_all_pt_concat_reconstructions['all_pt_fourth_labels'], return_counts= True))
print(np.unique(new_all_pt_concat_reconstructions['all_pt_fifth_labels'], return_counts= True))
print(np.unique(new_all_pt_concat_reconstructions['all_pt_fifth_detail_labels'], return_counts= True))

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW MEAN VERSION - DOMINIO DEL TEMPO

                                                LE WINDOWS SONO DIZIONARI!
                                                
                                                    EEG WAVELET FEATURES
'''

'''
Nell'implementazione attuale, 
le posizioni sull'asse x (window_mid_points_in_ms) rappresentano 
i punti temporali corrispondenti al centro di ciascuna finestra. 

Quindi, ogni etichetta sull'asse x indica la metà temporale della rispettiva finestra in millisecondi.

'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)


# Definisci una mappa di colori per i classificatori
color_map = {
    'logistic_regression': 'green',
    'xgboost': 'purple',
    'svm': 'blue'
}


familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def calculate_chance_level(labels):
    unique_values, labels_counts = np.unique(labels, return_counts=True)
    num_folds = 5 
    total_labels = np.sum(labels_counts)
    elements_per_fold = total_labels / num_folds
    rounded_elements_per_fold = math.floor(elements_per_fold)
    class_percentage = labels_counts / total_labels * 100
    highest_class_percentage = max(class_percentage)
    samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
    exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
    baseline_accuracy = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
    return baseline_accuracy

def plot_mean_best_scores_for_window(statistics_level_dict, level_str, save_path):
    
   # Calcola il livello di chance usando le etichette concatenate in new_all_pt_concat_reconstructions
    baseline_accuracy_highest_class_in_fold = calculate_chance_level(all_labels)

    # Crea la cartella principale 'mean_wavelet_levels' dentro 'patients'
    mean_wavelet_levels_path = os.path.join(save_path, 'mean_wavelet_levels', 'patients')
    os.makedirs(mean_wavelet_levels_path, exist_ok=True)
    
    # Crea una lista per le finestre
    #n_windows = list(statistics_level_dict[next(iter(statistics_level_dict))]['logistic_regression'].keys())

    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    
    # Inizializzo le medie per ogni classificatore
    mean_scores = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}
    ci_low = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}
    ci_high = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}

    # Per ogni classificatore e finestra, prendi la media e l'intervallo di confidenza dal dizionario
    for classifier in ['logistic_regression', 'xgboost', 'svm']:
        
        for window in n_windows:
            
            # Estrai la media e l'intervallo di confidenza dai dati
            mean_scores[classifier].append(statistics_level_dict[classifier][window]['mean'])
            ci_low[classifier].append(statistics_level_dict[classifier][window]['ci_lower'])
            ci_high[classifier].append(statistics_level_dict[classifier][window]['ci_upper'])
        
        
    # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
    window_starts_samples = []
    window_ends_samples = []
    window_mid_points_samples = []

    # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
    start_sample = 0

    while start_sample + window_size_samples <= n_samples:
        end_sample = start_sample + window_size_samples
        window_starts_samples.append(start_sample)
        window_ends_samples.append(end_sample)
        window_mid_points_samples.append(start_sample + window_size_samples // 2)
        start_sample += stride_samples

    # Conversione dei punti in millisecondi
    window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
    window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
    window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    # Inizio del plot
    plt.figure(figsize=(10, 7))

    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''PER CAMBIO RAPPRESENTAZIONE DA DOMINIO FINESTRE A DOMINIO DEL TEMPO'''
    
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)
    
    plt.xticks(window_mid_points_in_ms, [f'{int(pos)}' for pos in window_mid_points_in_ms])
    
    plt.tick_params(axis='x', labelsize=12)
    plt.tick_params(axis='y', labelsize=12)
    
     # Aggiungi i punteggi medi dei classificatori e gli intervalli di confidenza
    for classifier in ['logistic_regression', 'xgboost', 'svm']:
        plt.plot(window_mid_points_in_ms, mean_scores[classifier], label=f'{classifier}', color=color_map[classifier])
        plt.fill_between(window_mid_points_in_ms, ci_low[classifier], ci_high[classifier], alpha=0.1, color=color_map[classifier])

    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')

    # Traccia la linea orizzontale della chance level
    baseline_accuracy_highest_class_in_fold = calculate_chance_level(all_labels)
    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level')
    
    # Aggiunge il livello di baseline in base al livello specificato
    if level_str == '4':
        plt.title(f"Patients' Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level_str} - Θ+δ Range")
        plt.ylim(0.28, 0.41)
    elif level_str == '5':
        plt.title(f"Patients' Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level_str} - δ Range")
        plt.ylim(0.28, 0.41)
    elif level_str == '5_detail':
        plt.title(f"Patients' Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level_str} - Θ Range")
        plt.ylim(0.28, 0.41)

    plt.xlabel('Time (mms)', fontweight='bold', fontsize = 12)
    plt.ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 12)

    #plt.legend(loc='best')
    plt.legend(prop={'weight': 'bold', 'size': 9}, loc='best')

    plt.grid(True)
    
    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_pts_level_{level_str}_time_domain.png'  # Usa level invece di level_str
    save_file_path = os.path.join(save_path, 'mean_wavelet_levels', 'patients', filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'Plot salvato in: \033[1m{save_file_path}\033[0m\n')

# Esempio di utilizzo
all_labels = new_all_pt_concat_reconstructions['all_pt_fourth_labels']
save_path = f'/home/stefano/Interrogait/{familiar_path}/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_4, '4', save_path)
plot_mean_best_scores_for_window(statistics_level_5, '5', save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail, '5_detail', save_path)


##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE EEG FILTERED 1-20 Hz DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) PER LA RELATIVA FINESTRA TESTATA**

In [ ]:
#Library Importing 
    
import os
import math
import copy as cp 

import tqdm

import mne 
import scipy

import numpy as np  # NumPy per operazioni numeriche
import matplotlib.pyplot as plt  # Matplotlib per la isualizzazione dei dati
from sklearn.model_selection import train_test_split

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
import pickle 

# Carico il dizionario dei dati concatenati di ogni singolo soggetto, salvato con pickle
with open('/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)

In [ ]:
import os

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def process_txt_files(base_path, classifiers, n_windows):
    
    best_scores_filtered_1_20_all_classifiers_pt = {}
    
    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(base_path, classifier, "EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/single_patient_optimized_params_1_20")
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)
                
                # Escludi i file che contengono "invalid_params", "all_pt_level_4", o "all_pt_level_5"
                if "invalid_params" in file_name or 'all_pt_level_4' in file_name or 'all_pt_level_5' in file_name:
                    continue
                
                # Determina il livello dal nome del file
                #if "_level_approx_4_std" in file_name:
                #    level = 'approx_4'
                #elif "_level_approx_5_std" in file_name:
                #    level = 'approx_5'
                #elif "_level_detail_5_std" in file_name:  # Nuova condizione per i coefficienti di dettaglio
                #    level = "detail_5"
                #else:
                #    continue  # Salta il file se non è né livello 4 né livello 5
                
                # Determina il livello dal nome del file
                if "filtered_1_20_std" in file_name:
                    level = 'filtered_1_20'
                else:
                    continue  # Salta il file se non è né livello 4 né livello 5
            
            
                # Verifica che il file sia per uno specifico soggetto (th_1, th_2, ..., th_15)
                subject = None
                if "pt_" in file_name:
                    try:
                        subject = file_name.split("pt_")[1].split("_")[0]  # Estrai il numero del soggetto (1-15)
                        subject = int(subject)  # Converte in intero per verificare che sia un numero valido
                        subject_key = f"pt_{subject}"  # Se tutto va bene, crea la chiave
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue  # Se c'è un errore, passa al prossimo file
                
                # Se il file è di tipo "approx_4"
                if level == 'filtered_1_20':
                    
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_filtered_1_20_all_classifiers_pt: 
                        best_scores_filtered_1_20_all_classifiers_pt[subject_key] = {}

                    if classifier not in best_scores_filtered_1_20_all_classifiers_pt[subject_key]:
                        best_scores_filtered_1_20_all_classifiers_pt[subject_key][classifier] = {}

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_filtered_1_20_all_classifiers_pt[subject_key][classifier][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break

               
    return best_scores_filtered_1_20_all_classifiers_pt

# Definisci il path base e le cartelle dei classificatori
base_path = f"/home/stefano/Interrogait/{familiar_path}"
classifiers = ["logistic_regression", "xgboost", "svm"]

# Lista dinamica delle finestre (0-50, 25-75, ..., 250-300)
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiama la funzione per processare i file e ottenere i best scores
best_scores_filtered_1_20_all_classifiers_pt = process_txt_files(base_path, classifiers, n_windows)

# Stampa i risultati
print("\033[1mbest_scores_filtered_1_20_all_classifiers_pt.keys()\033[0m:", best_scores_filtered_1_20_all_classifiers_pt.keys())


In [ ]:
print(best_scores_filtered_1_20_all_classifiers_pt['pt_16'].keys())
print(best_scores_filtered_1_20_all_classifiers_pt['pt_16']['svm'].keys())
print(best_scores_filtered_1_20_all_classifiers_pt['pt_16']['svm']['0-50'])

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA PER OGNI CLASSIFIER - NEW VERSION


Spiegazione delle modifiche

- Parametro classifier nella funzione: La funzione calculate_mean_and_confidence_interval ora 
prende un parametro aggiuntivo classifier, in modo che possa calcolare le statistiche 
per un classificatore specifico all'interno della struttura best_scores.

- Raccolta dei punteggi: All'interno della funzione, per ogni finestra (window), 
raccogli i punteggi di tutti i soggetti per il classificatore specificato.

- Dizionari annidati: statistics_level_4, statistics_level_5 e statistics_level_5_detail sono ora
dizionari annidati, dove ogni classificatore ha il proprio dizionario di risultati per le varie finestre temporali.


Ecco un esempio di come apparirebbe statistics_level_4:

statistics_level_4 = {
    "logistic_regression": {
        "0-50": {
            "mean": 0.78,
            "ci_lower": 0.75,
            "ci_upper": 0.81
        },
        "25-75": {
            "mean": 0.82,
            "ci_lower": 0.79,
            "ci_upper": 0.85
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.76,
            "ci_lower": 0.72,
            "ci_upper": 0.80
        }
    },
    "xgboost": {
        "0-50": {
            "mean": 0.80,
            "ci_lower": 0.77,
            "ci_upper": 0.83
        },
        "25-75": {
            "mean": 0.84,
            "ci_lower": 0.81,
            "ci_upper": 0.87
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.79,
            "ci_lower": 0.75,
            "ci_upper": 0.83
        }
    },
    "svm": {
        "0-50": {
            "mean": 0.77,
            "ci_lower": 0.74,
            "ci_upper": 0.80
        },
        "25-75": {
            "mean": 0.81,
            "ci_lower": 0.78,
            "ci_upper": 0.84
        },
        # Altre finestre temporali...
        "250-300": {
            "mean": 0.75,
            "ci_lower": 0.71,
            "ci_upper": 0.79
        }
    }
}
'''

import numpy as np
import scipy.stats as stats

n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
             "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, classifier, windows, confidence_level = 0.95):
    """
    Calcola la media e l'intervallo di confidenza al livello desiderato per ogni finestra e
    organizza i risultati in un dizionario per un classificatore specifico.
    """
    results = {}

    for window in windows:
        # Raccogli tutti i best scores per questa finestra da tutti i soggetti per il classificatore specificato
        scores = [subject_scores[classifier][window] 
                  for subject_scores in best_scores.values() 
                  if window in subject_scores[classifier]]
        
        # Calcola la media
        mean_score = np.mean(scores)
        
        # Calcola la deviazione standard
        std_dev = np.std(scores, ddof=1)
        
        # Numero di soggetti
        n = len(scores)
        
        # Calcola l'intervallo di confidenza
        confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
        
        # Salva i risultati per la finestra specifica
        results[window] = {
            'mean': mean_score,
            'ci_lower': confidence_interval[0],
            'ci_upper': confidence_interval[1]
        }

    return results

# Esegui la funzione per ciascun classificatore nei best scores di livello 4
statistics_level_1_20 = {
    classifier: calculate_mean_and_confidence_interval(best_scores_filtered_1_20_all_classifiers_pt, classifier, n_windows)
    for classifier in ["logistic_regression", "xgboost", "svm"]
}


# Funzione per stampare i risultati con i classificatori in grassetto
def print_bold_statistics(statistics):
    for classifier in statistics:
        print(f"\033[1m{classifier}\033[0m")  # Stampa il nome del classificatore in grassetto
        for window, stats in statistics[classifier].items():
            print(f"  {window}: Mean = {stats['mean']:.2f}, CI Lower = {stats['ci_lower']:.2f}, CI Upper = {stats['ci_upper']:.2f}")

# Stampa i risultati per ciascun livello
print("Risultati per il livello EEG preprocessed 1-20Hz:")
print_bold_statistics(statistics_level_1_20)

In [ ]:
type(statistics_level_1_20)

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''

import pickle

path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_subject_level_concatenations_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_pt_1_20 = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_all_pt_concat_reconstructions_1_20.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions_1_20 = pickle.load(f)  

In [ ]:
new_subject_level_concatenations_pt_1_20['pt_1'].keys()

In [ ]:
new_all_pt_concat_reconstructions_1_20.keys()

In [ ]:
print(new_all_pt_concat_reconstructions_1_20['labels'].shape)
print()
print(np.unique(new_all_pt_concat_reconstructions_1_20['labels'], return_counts= True))

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW MEAN VERSION - DOMINIO DEL TEMPO

Nell'implementazione attuale, 
le posizioni sull'asse x (window_mid_points_in_ms) rappresentano 
i punti temporali corrispondenti al centro di ciascuna finestra. 

Quindi, ogni etichetta sull'asse x indica la metà temporale della rispettiva finestra in millisecondi.

'''

import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)

# Definisci una mappa di colori per i classificatori
color_map = {
    'logistic_regression': '#006400',
    'xgboost': '#FF00FF',
    'svm': '#00BFFF',
}

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def calculate_chance_level(labels):
    unique_values, labels_counts = np.unique(labels, return_counts=True)
    num_folds = 5 
    total_labels = np.sum(labels_counts)
    elements_per_fold = total_labels / num_folds
    rounded_elements_per_fold = math.floor(elements_per_fold)
    class_percentage = labels_counts / total_labels * 100
    highest_class_percentage = max(class_percentage)
    samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
    exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
    baseline_accuracy = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
    return baseline_accuracy

def plot_mean_best_scores_for_window(statistics_level_dict, level_str, save_path):
    
   # Calcola il livello di chance usando le etichette concatenate in new_all_th_concat_reconstructions
    baseline_accuracy_highest_class_in_fold = calculate_chance_level(all_labels)

    # Crea la cartella principale 'mean_wavelet_levels' dentro 'therapists'
    mean_filtered_1_20_path = os.path.join(save_path, 'mean_filtered_1_20', 'patients')
    os.makedirs(mean_filtered_1_20_path, exist_ok=True)
    

    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Inizializzo le medie per ogni classificatore
    mean_scores = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}
    ci_low = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}
    ci_high = {classifier: [] for classifier in ['logistic_regression', 'xgboost', 'svm']}

    # Per ogni classificatore e finestra, prendi la media e l'intervallo di confidenza dal dizionario
    for classifier in ['logistic_regression', 'xgboost', 'svm']:
        
        for window in n_windows:
            
            # Estrai la media e l'intervallo di confidenza dai dati
            mean_scores[classifier].append(statistics_level_dict[classifier][window]['mean'])
            ci_low[classifier].append(statistics_level_dict[classifier][window]['ci_lower'])
            ci_high[classifier].append(statistics_level_dict[classifier][window]['ci_upper'])
        
        
    # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
    window_starts_samples = []
    window_ends_samples = []
    window_mid_points_samples = []

    # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
    start_sample = 0

    while start_sample + window_size_samples <= n_samples:
        end_sample = start_sample + window_size_samples
        window_starts_samples.append(start_sample)
        window_ends_samples.append(end_sample)
        window_mid_points_samples.append(start_sample + window_size_samples // 2)
        start_sample += stride_samples

    # Conversione dei punti in millisecondi
    window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
    window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
    window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]


    # Inizio del plot
    plt.figure(figsize=(10, 7))

    # Creiamo le etichette per le finestre
    window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
    tick_positions = window_mid_points_in_ms
    
    '''PER CAMBIO RAPPRESENTAZIONE DA DOMINIO FINESTRE A DOMINIO DEL TEMPO'''
    # Imposta le etichette principali
    #plt.xticks(tick_positions, window_labels)
    
    plt.xticks(window_mid_points_in_ms, [f'{int(pos)}ms' for pos in window_mid_points_in_ms])

    plt.tick_params(axis='x', labelsize=12)
    plt.tick_params(axis='y', labelsize=12)

     # Aggiungi i punteggi medi dei classificatori e gli intervalli di confidenza
    for classifier in ['logistic_regression', 'xgboost', 'svm']:
        plt.plot(window_mid_points_in_ms, mean_scores[classifier], label=f'{classifier}', color=color_map[classifier])
        plt.fill_between(window_mid_points_in_ms, ci_low[classifier], ci_high[classifier], alpha=0.1, color=color_map[classifier])

    # Linea verticale tratteggiata per il campione 50 (prestimolo)
    plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')

    # Traccia la linea orizzontale della chance level
    baseline_accuracy_highest_class_in_fold = calculate_chance_level(all_labels)
    plt.axhline(y=baseline_accuracy_highest_class_in_fold, color='red', linestyle='--', label=f'Chance Level')
    
    # Aggiunge il livello di baseline in base al livello specificato    
    plt.title(f"Patients' Mean Best Accuracy Score for Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG preprocessed 1-20Hz")
    plt.ylim(0.28, 0.43)
    level_str = 'filtered_1_20'
    
    plt.xlabel('Time (mms)', fontweight='bold', fontsize = 12)
    plt.ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 12)

    #plt.legend(loc='best')
    plt.legend(prop={'weight': 'bold', 'size': 9}, loc='best')

    plt.grid(True)
    
    #plt.show()

    # Salva il plot nel percorso specifico
    filename = f'mean_best_scores_all_pts_level_{level_str}_time_domain.png'  # Usa level invece di level_str
    save_file_path = os.path.join(save_path, 'mean_filtered_1_20', 'patients', filename)
    plt.savefig(save_file_path, bbox_inches='tight')
    plt.close()
    print(f'Plot salvato in: \033[1m{save_file_path}\033[0m\n')

# Esempio di utilizzo
all_labels = new_all_pt_concat_reconstructions_1_20['labels']
save_path = f'/home/stefano/Interrogait/{familiar_path}/all_classifiers_plots/EEG_4_classes_1_20Hz/EEG_50_window_25_overlap/'

plot_mean_best_scores_for_window(statistics_level_1_20, 'filtered_1_20', save_path)

#### **All Patients (PT01-PT20)**

### Plots of **Grand Average Mean** of Best Single Subject's Accuracy Score Performances 

#### **Coupled Experimental Conditions**

- ##### Obtained for **EACH window**
- ##### Separated by **EACH level of reconstruction (θ+δ, δ and θ)**

##### **Indicazioni per Codice da Implementare**

Per **ogni soggetto**, tu avrai sostanzialmente **18 file**... che appartengono allo stesso soggetto, ma **riferiti ad un certo livello di ricostruzione del segnale**... i livelli di ricostruzione (che son **3**) son **identificati da** alcune stringhe nel file che son

- **level_approx_4**
- **level_approx_5**
- **level_detail_5**

Ora, queste identificano il livello di ricostruzione utilizzato e fornito al diverso classificatore per l'identificazione dei correlati neurali dei livelli di responsabilità...

Poi, sempre **nella stessa stringa** che compone il **nome del file**, ci sono **altre stringhe** che invece identificano invece la **condizione sperimentale a cui è associato il file**, che son 6, ossia

- baseline_vs_th_resp
- baseline_vs_pt_resp
- baseline_vs_shared_resp
- th_resp_vs_shared_resp
- pt_resp_vs_shared_resp
- th_resp_vs_pt_resp

Queste, invece, identificano sostanzialmente la condizione sperimentale..
Questo vuol dire che, per ogni soggetto, avrò come ti avevo detto 18 file, divisi in 3 gruppi diciamo per il livello di ricostruzione e poi ogni livello di ricostruzione avrà 6 condizioni sperimentali di file associate...

Ora, io vorrei che **i dizionari che mi crei** nel codice che ti ho fornito siano sempre con una simile struttura, dove avrò

Ognuna delle tre variabili vorrei che avesse questa struttura annidata, ossia:

- soggetti (th_)* 
 - classifier, 
  - MA POI va inclusa la chiave che indentifica la "condizione sperimentale" (ossia una tra queste:
    **baseline_vs_th_resp**; **baseline_vs_pt_resp**; **baseline_vs_shared_resp**; **th_resp_vs_shared_resp**;
    **pt_resp_vs_shared_resp**; **th_resp_vs_pt_resp**)  
   - e finestra testata...

Ognuna di queste variabili, vorrei che contenesse secondo questa logica, ossia  
    
**il best score ottenuto sulla specifica finestra, tramite uno specifico classificatore, avendo adottato uno specifico livello di ricostruzione del segnale EEG, per una specifica condizione sperimentale per ogni soggetto**


Quello che deve essere modificato, secondo me, è innanzitutto 

1) la logica di estrazione delle stringhe che identificano per uno stesso soggetto, ossia i suoi dati associati ai tre livelli di ricostruzione, usati poi dentro i diversi classificatori... ossia 

- level_approx_4
- level_approx_5
- level_detail_5

(o forse già c'è sta roba)...

Dopodiché,  deve essere aggiunta anche 

2) la logica per l'identificazione per ogni file della condizione sperimentale associata, in modo da creare poi così le sottochiave associate le condizioni sperimentali... 

Di conseguenza, alla fine dovrei avere **tre dizionari annidati su diversi livelli**, ciascuno che conterrà, 
**per ogni specifico soggetto** (ovviamente ogni dizionario fa riferimento ad un certo livello di ricostruzione utilizzato), **il Best Score** che, ogni soggetto singolarmente, ha ottenuto sulla **specifica finestra**, rispetto al **confronto con una specifica coppia di condizioni sperimentali**, utilizzando uno **specifico classificatore**...



##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **COUPLED EXPERIMENTAL CONDITIONS**

In [ ]:
import os

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def process_txt_files(base_path, classifiers, n_windows):
    
    # Dizionari per ogni livello di ricostruzione
    best_scores_level_4 = {}
    best_scores_level_5 = {}
    best_scores_level_5_detail = {}

    # Condizioni sperimentali
    conditions = [
        "baseline_vs_th_resp",
        "baseline_vs_pt_resp",
        "baseline_vs_shared_resp",
        "th_resp_vs_shared_resp",
        "pt_resp_vs_shared_resp",
        "th_resp_vs_pt_resp"
    ]

    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(
            base_path, classifier, 
            "EEG_2_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/single_patient_optimized_params_coupled_exp_cond"
        )
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            
            if file_name.endswith(".txt"):
                
                file_path = os.path.join(classifier_path, file_name)

                # Determina il livello dal nome del file
                if "_level_approx_4" in file_name:
                    level = 'approx_4'
                    #target_dict = best_scores_level_4
                elif "_level_approx_5" in file_name:
                    level = 'approx_5'
                    #target_dict = best_scores_level_5
                elif "_level_detail_5" in file_name:
                    level = "detail_5"
                    #target_dict = best_scores_level_5_detail
                else:
                    continue  # Salta il file se non è un livello valido

                # Estrai il soggetto
                subject = None
                if "pt_" in file_name:
                    try:
                        subject = file_name.split("pt_")[1].split("_")[0]
                        subject = int(subject)
                        subject_key = f"pt_{subject}"
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue
                
                # Estrai la condizione sperimentale
                condition = None
                for cond in conditions:
                    if cond in file_name:
                        condition = cond
                        break
                if not condition:
                    print(f"Nessuna condizione valida trovata per il file: {file_name}")
                    continue

                # Se il file è di tipo "approx_4"
                if level == 'approx_4':
                    
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_4:
                        best_scores_level_4[subject_key] = {}

                    if classifier not in best_scores_level_4[subject_key]:
                        best_scores_level_4[subject_key][classifier] = {}
                    
                    if condition not in best_scores_level_4[subject_key][classifier]:
                        best_scores_level_4[subject_key][classifier][condition] = {}
                        
                        
                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                
                                if window not in best_scores_level_4[subject_key][classifier][condition]:
                                    best_scores_level_4[subject_key][classifier][condition][window] = {}
                                    
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_4[subject_key][classifier][condition][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break

                # Se il file è di tipo "approx_5"
                elif level == 'approx_5':
                    
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5:
                        best_scores_level_5[subject_key] = {}

                    if classifier not in best_scores_level_5[subject_key]:
                        best_scores_level_5[subject_key][classifier] = {}
                        
                    if condition not in best_scores_level_5[subject_key][classifier]:
                        best_scores_level_5[subject_key][classifier][condition] = {}
                        
                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                
                                if window not in best_scores_level_5[subject_key][classifier][condition]:
                                    best_scores_level_5[subject_key][classifier][condition][window] = {}
                                    
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5[subject_key][classifier][condition][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break
                
                # Se il file è di tipo "detail_5"
                elif level == 'detail_5':
                    
                    # Crea la struttura del dizionario se non esiste
                    if subject_key not in best_scores_level_5_detail:
                        best_scores_level_5_detail[subject_key] = {}

                    if classifier not in best_scores_level_5_detail[subject_key]:
                        best_scores_level_5_detail[subject_key][classifier] = {}
                        
                    if condition not in best_scores_level_5_detail[subject_key][classifier]:
                        best_scores_level_5_detail[subject_key][classifier][condition] = {}
                        

                    # Leggi il file .txt
                    with open(file_path, 'r') as f:
                        lines = f.readlines()

                        # Cerca la riga che inizia con "Best Score for Window" e il valore float
                        for line in lines:
                            for window in n_windows:
                                if window not in best_scores_level_5_detail[subject_key][classifier][condition]:
                                    best_scores_level_5_detail[subject_key][classifier][condition][window] = {}
                                if f"Best Score for Window {window}:" in line:
                                    try:
                                        score = float(line.split(":")[1].strip())
                                        best_scores_level_5_detail[subject_key][classifier][condition][window] = score
                                    except ValueError:
                                        print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                    break


    return best_scores_level_4, best_scores_level_5, best_scores_level_5_detail

# Configurazione dei parametri
base_path = f"/home/stefano/Interrogait/{familiar_path}"
classifiers = ["logistic_regression", "xgboost", "svm"]
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiamata della funzione
best_scores_level_4_pt_all_classifiers_coupled_exp, best_scores_level_5_pt_all_classifiers_coupled_exp, best_scores_level_5_detail_pt_all_classifiers_coupled_exp = process_txt_files(base_path, classifiers, n_windows)

# Output dei risultati
print("\033[1mbest_scores_level_4_pt_all_classifiers_coupled_exp.keys()\033[0m:", best_scores_level_4_pt_all_classifiers_coupled_exp.keys())
print("\033[1mbest_scores_level_5_pt_all_classifiers_coupled_exp.keys()\033[0m:", best_scores_level_5_pt_all_classifiers_coupled_exp.keys())
print("\033[1mbest_scores_level_5_detail_pt_all_classifiers_coupled_exp.keys()\033[0m:", best_scores_level_5_detail_pt_all_classifiers_coupled_exp.keys())


In [ ]:
print(type(best_scores_level_4_pt_all_classifiers_coupled_exp))
print()
print(best_scores_level_4_pt_all_classifiers_coupled_exp.keys())
print()
print(best_scores_level_4_pt_all_classifiers_coupled_exp['pt_1'].keys())
print()
print(best_scores_level_4_pt_all_classifiers_coupled_exp['pt_1']['xgboost'].keys())
print()
print(best_scores_level_4_pt_all_classifiers_coupled_exp['pt_1']['xgboost']['baseline_vs_th_resp'].keys())
print()
print(best_scores_level_4_pt_all_classifiers_coupled_exp['pt_1']['svm']['baseline_vs_th_resp']['0-50'])
print()
#print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1']['svm']['baseline_vs_th_resp']['0-50'])

In [ ]:
#print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])
#print()
#print(best_scores_level_5_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])
#print()
#print(best_scores_level_5_detail_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])

In [ ]:
for subject, subject_scores in best_scores_level_5_detail_pt_all_classifiers_coupled_exp.items():
    for classifier, classifier_scores in subject_scores.items():
        for comparison, comparison_scores in classifier_scores.items():
            for window, value in comparison_scores.items():
                if not isinstance(value, (int, float)):
                    print(f"Invalid value found: Subject={subject}, Classifier={classifier}, Comparison={comparison}, Window={window}, Value={value}")

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA PER OGNI CLASSIFIER - NEW VERSION


Cosa fa il codice:
Funzione calculate_mean_and_confidence_interval:

Calcola la media e l'intervallo di confidenza per ogni finestra per ogni confronto 
(per esempio, baseline_vs_th_resp, th_resp_vs_pt_resp, etc.) e classificatore.

Raggruppa i risultati per confronto e finestra temporale.
Calcolo delle statistiche:

Per ciascun livello di ricostruzione (4, 5, 5 dettagliato), la funzione calcola le statistiche per ogni classificatore.
Usa il dizionario con i punteggi migliori (best_scores_level_4_th_all_classifiers_coupled_exp, etc.).

Stampa dei risultati:

La funzione print_bold_statistics stampa i risultati per ogni classificatore, 
confronto e finestra con la media e l'intervallo di confidenza.

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 
Filtra i dati:

Per un classificatore specifico (ad esempio logistic_regression, xgboost, svm).
Per una condizione sperimentale specifica (ad esempio baseline_vs_th_resp).
Per una finestra temporale specifica (ad esempio 0-50).
Raccoglie i Best Score di tutti i soggetti:

Esamina i punteggi per la stessa finestra temporale.
Include solo i soggetti che hanno un punteggio per quel classificatore, quella condizione e quella finestra.
Calcola la statistica:

Media dei punteggi raccolti.
Deviazione standard.
Intervallo di confidenza (CI) al livello di confidenza desiderato (default: 95%), utilizzando la distribuzione t di Student.


Il risultato finale sarà un dizionario annidato, organizzato secondo i seguenti livelli:

Classificatore (ad esempio: logistic_regression, xgboost, svm).
Condizione sperimentale (ad esempio: baseline_vs_th_resp, th_resp_vs_pt_resp).
Finestra temporale (ad esempio: 0-50, 25-75).
Statistiche:
mean: la media dei punteggi.
ci_lower: il limite inferiore dell'intervallo di confidenza.
ci_upper: il limite superiore dell'intervallo di confidenza.

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 
STRUTTURA RISULTANTE

{
    "logistic_regression": {
        "baseline_vs_th_resp": {
            "0-50": {"mean": 0.82, "ci_lower": 0.78, "ci_upper": 0.86},
            "25-75": {"mean": 0.85, "ci_lower": 0.81, "ci_upper": 0.89},
            "50-100": {"mean": 0.80, "ci_lower": 0.76, "ci_upper": 0.84},
            ...
        },
        "th_resp_vs_pt_resp": {
            "0-50": {"mean": 0.75, "ci_lower": 0.70, "ci_upper": 0.80},
            "25-75": {"mean": 0.78, "ci_lower": 0.73, "ci_upper": 0.83},
            ...
        },
        ...
    },
    "xgboost": {
        "baseline_vs_th_resp": {
            "0-50": {"mean": 0.88, "ci_lower": 0.84, "ci_upper": 0.92},
            "25-75": {"mean": 0.87, "ci_lower": 0.83, "ci_upper": 0.91},
            ...
        },
        ...
    },
    "svm": {
        ...
    }
}

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 

'''

import numpy as np
import scipy.stats as stats

# Definizione delle finestre temporali
n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
             "150-200", "175-225", "200-250", "225-275", "250-300"]



def calculate_mean_and_confidence_interval(best_scores, classifier, windows, comparisons, confidence_level=0.95):
    """
    Calcola la media e l'intervallo di confidenza per ogni finestra e condizione sperimentale 
    per un classificatore specifico e raccoglie i risultati in un dizionario.
    """
    results = {}

    for comparison in comparisons:
        comparison_results = {}  # Risultati per un confronto specifico

        for window in windows:
            # Raccogli tutti i best scores per questa finestra da tutti i soggetti per il classificatore specificato
            scores = [subject_scores[classifier][comparison][window] 
                      for subject_scores in best_scores.values() 
                      if comparison in subject_scores[classifier] and window in subject_scores[classifier][comparison]]
            
            #print(type(scores))
            
            if scores:  # Se ci sono punteggi
                
                # Calcola la media
                mean_score = np.mean(scores)
                
                # Calcola la deviazione standard
                std_dev = np.std(scores, ddof=1)
                
                # Numero di soggetti
                n = len(scores)
                
                # Calcola l'intervallo di confidenza
                confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
                
                # Salva i risultati per la finestra specifica e il confronto
                comparison_results[window] = {
                    'mean': mean_score,
                    'ci_lower': confidence_interval[0],
                    'ci_upper': confidence_interval[1]
                }
        
        # Salva i risultati per il confronto
        results[comparison] = comparison_results

    return results


# Classificatori e confronti da usare
classifiers = ["logistic_regression", "xgboost", "svm"]

comparisons = ['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 
               'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp']

# Calcolare le statistiche per ciascun livello
statistics_level_4_pt_fam = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_4_pt_all_classifiers_coupled_exp, classifier, n_windows, comparisons)
    for classifier in classifiers}

statistics_level_5_pt_fam = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_5_pt_all_classifiers_coupled_exp, classifier, n_windows, comparisons)
    for classifier in classifiers}

statistics_level_5_detail_pt_fam = {
    classifier: calculate_mean_and_confidence_interval(best_scores_level_5_detail_pt_all_classifiers_coupled_exp, classifier, n_windows, comparisons)
    for classifier in classifiers}

# Funzione per stampare i risultati con i classificatori in grassetto
def print_bold_statistics(statistics):
    for classifier in statistics:
        print(f"\n\033[1m{classifier}\033[0m\n")  # Stampa il nome del classificatore in grassetto
        for comparison in statistics[classifier]:
            print(f"  \n\033[1m{comparison}\033[0m")  # Stampa il confronto in grassetto
            for window, stats in statistics[classifier][comparison].items():
                print(f"    {window}: Mean = {stats['mean']:.2f}, CI Lower = {stats['ci_lower']:.2f}, CI Upper = {stats['ci_upper']:.2f}")

                # Stampa i risultati per ciascun livello
#print("\t\t\tRisultati per il \033[1mlivello 4 coeff approx\033[0m:")
#print_bold_statistics(statistics_level_4_pt_fam)

#print("\n\n\t\t\tRisultati per il \033[1mlivello 5 coeff approx\033[0m:")
#print_bold_statistics(statistics_level_5_pt_fam)

#print("\n\n\t\t\tRisultati per il \033[1mlivello 5 coeff detail\033[0m:")
#print_bold_statistics(statistics_level_5_detail_pt_fam)




In [ ]:
type(statistics_level_4_pt_fam)

In [ ]:
cd ..

In [ ]:
!pwd

In [ ]:
cd New_Plots_Sliding_Estimator_MNE

In [ ]:
print(statistics_level_4_pt_fam.keys())
print()
print(statistics_level_4_pt_fam['svm'].keys())
print()
print(statistics_level_4_pt_fam['svm']['baseline_vs_th_resp'].keys())
print()
print(statistics_level_4_pt_fam['svm']['baseline_vs_th_resp']['0-50'].keys())
print()
print()
print(statistics_level_4_pt_fam['svm']['baseline_vs_th_resp']['0-50'])
print()
#print(statistics_level_4_th_fam['svm']['baseline_vs_th_resp']['0-50'])

In [ ]:
#Salvo le statitiche di ogni finestra per le mie ricostruzioni  4°, 5° e 4+5° livello  

''' PATH  --> cd Plots_Sliding_Estimator_MNE '''

import pickle

# Salvare l'intero dizionario annidato con pickle

base_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'

with open(f'{base_path}/statistics_level_4_pt_fam.pkl', 'wb') as f:
    pickle.dump(statistics_level_4_pt_fam, f)
    
with open(f'{base_path}/statistics_level_5_pt_fam.pkl', 'wb') as f:
    pickle.dump(statistics_level_5_pt_fam, f)
    
with open(f'{base_path}/statistics_level_5_detail_pt_fam.pkl', 'wb') as f:
    pickle.dump(statistics_level_5_detail_pt_fam, f)

In [ ]:
'''               
                        DA QUI IN GIU' BISOGNA UN ATTIMO RAGIONARE! 
    
      DATO CHE IO ORA DOVREI ITERARE RISPETTO A TUTTE LE CONCATENAZIONI MEDIE DI 
      
      OGNI COPPIA DI CONDIZIONI SPERIMETALI CONFRONTATE A COPPIE OSSIA
      
      1) BASELINE_VS_TH_RESP
      2) BASELINE_VS_PT_RESP
      3) BASELINE_VS_SHARED_RESP
      
      4) TH_VS_PT_RESP
      5) TH_VS_SHARED_RESP
      6) PT_RESP_VS_SHARED_RESP
      
      
      ORA, IO HO QUESTE STRUTTURE DATI???
      
      
'''

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''


''' QUESTA VARIABILE NON MI INTERESSA, DATO CHE CONTIENE 
        I DATI CONCATENATI SI', DEL SINGOLO SOGGETTO (CHE MI INTERESSA!),
                    MA PER TUTTE E 4 LE CONDIZIONI SPERIMENTALI INSIEME, OSSIA:
                    
                    1) BASELINE
                    2) TH_RESP
                    3) PT_RESP
                    4) SHARED_RESP
                    
                    ED INVECE A ME INTERESSA PRENDERE
                    I DATI DELLE COPPIE DI CONDIZIONI SPERIMENTALI DEL SINGOLO SOGGETTO!
                    
                    OSSIA
                    
                      1) BASELINE_VS_TH_RESP
                      2) BASELINE_VS_PT_RESP
                      3) BASELINE_VS_SHARED_RESP

                      4) TH_VS_PT_RESP
                      5) TH_VS_SHARED_RESP
                      6) PT_RESP_VS_SHARED_RESP
      
                    
'''    

import pickle

path = f'/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_th'''

print(new_subject_level_concatenations_pt.keys())
print()
print(new_subject_level_concatenations_pt['pt_1'].keys())
print()
print(new_subject_level_concatenations_pt['pt_1']['theta'].shape)

In [ ]:
'''ANCHE QUESTA NON MI INTERESSA, DATO CHE CONTIENE I DATI CONCATENATI, DI TUTTI I SOGGETTI, 
PER TUTTE E 4 LE CONDIZIONI SPERIMENTALI!'''

path = f'/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_all_pt_concat_reconstructions.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions = pickle.load(f)  

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_all_th_concat_reconstructions'''

print(new_all_pt_concat_reconstructions.keys())
print()
print(new_all_pt_concat_reconstructions['all_pt_fourth_labels'].shape)

In [ ]:
'''QUESTA, INVECE, POTREBBE DIVENTARE LA VARIABILE DI PARTENZA CHE CI INTERESSA,

DATO CHE CONTIENE I DATI CONCATENATI PER OGNI SOGGETTO,

RISPETTO ALLA COPPIA DI CONDIZIONI SPERIMENTALI CHE STIAMO CONFRONTANDO!!!
'''

path = f'/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_subject_level_concatenations_coupled_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt = pickle.load(f)  


In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_coupled_exp_th'''

print(new_subject_level_concatenations_coupled_exp_pt.keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt['pt_1'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp']['data'].shape)
print()
print(np.unique(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_pt_resp']['labels'], return_counts = True))

In [ ]:
'''QUESTA, INVECE, POTREBBE DIVENTARE LA VARIABILE DI PARTENZA CHE CI INTERESSA,

DATO CHE CONTIENE I DATI CONCATENATI PER OGNI SOGGETTO,

RISPETTO ALLA COPPIA DI CONDIZIONI SPERIMENTALI CHE STIAMO CONFRONTANDO!!!
'''

path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/'

# Caricare l'intero dizionario annidato con pickle
with open(f'{path}new_subject_level_concatenations_coupled_exp_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt_1_20 = pickle.load(f)  

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_coupled_exp_th'''

print(new_subject_level_concatenations_coupled_exp_pt_1_20.keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp']['data'].shape)
print()
print(np.unique(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp']['labels'], return_counts = True))

In [ ]:
'''ORA, QUELLO CHE INVECE CI SERVE CREARE, INVECE, 

SAREBBE LA VARIABILE CHE CONCATENA FRA TUTTI I SOGGETTI, I DATI E LE LABELS DELLA CHIAVE CHE IDENTIFICA
LA STESSA CONDIZIONE SPERIMENTALE SULLA QUALE STIAMO ITERANDO AL CICLO CORRENTE DEL FOR LOOP

SIA PER I DATI WAVELET, CHE PER I DATI 1-20!!!


Quindi, per ogni condizione sperimentale,
andiamo a concatenare tutti i dati e le etichette relativi a quella condizione,
ma provenienti da tutti i soggetti. 

Ogni condizione sperimentale ha già i dati e le etichette concatenati per ciascun soggetto,
e ora bisogna unire questi dati da tutti i soggetti per ogni condizione.

Immagina la struttura così:

Condizione sperimentale (per esempio, "condizione_1"):
Unire i dati di tutti i soggetti per la condizione "condizione_1".
Unire le etichette di tutti i soggetti per la condizione "condizione_1".


# La tua struttura dati originale
new_subject_level_concatenations_coupled_exp_th = {
    'subject_1': {
        'theta': {
            'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
            'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        'delta': {
            'condition_1': {'data': np.array([7, 8, 9]), 'labels': np.array([1, 1, 0])},
            'condition_2': {'data': np.array([10, 11, 12]), 'labels': np.array([0, 0, 1])}
        }
    },
    'subject_2': {
        'theta': {
            'condition_1': {'data': np.array([13, 14, 15]), 'labels': np.array([0, 1, 1])},
            'condition_2': {'data': np.array([16, 17, 18]), 'labels': np.array([1, 1, 0])}
        },
        'delta': {
            'condition_1': {'data': np.array([19, 20, 21]), 'labels': np.array([0, 0, 1])},
            'condition_2': {'data': np.array([22, 23, 24]), 'labels': np.array([1, 0, 1])}
        }
    }
}


ATTENZIONE! SICCOME IO ITERO ANCHE RISPETTO AI LIVELLI DI RICOSTRUZIONE, 
LE CONCATENAZIONI VENGANO FATTE PER 3 VOLTE (1 PER CIASCUN LIVELLO)

MA QUESTO RISULTA OVVIAMENTE ERRATO! 

DI CONSEGUENZA, PER CALCOLARE LE LABELS PER OGNI CONDIZIONE SPERIMENTALE, 

SI FA RIFERIMENTO A     "new_all_th_concat_reconstructions_coupled_exp_1_20"

- SIA PER I LIVELLI WAVELET 
- SIA PER IL "LIVELLO" EEG FILTERED 1-20

QUESTO PERCHÉ OVVIAMENTE LE LABELS NON È CHE SI 'RADDOPPIANO' SOLO PER IL FATTO CHE STO CONSIDERANDO
DIVERSI LIVELLI DI RICOSTRUZIONE, MA È SOLO PER TESTARE LE DIFFERENTI PERFORMANCE DI CLASSIFICAZIONE 
RISPETTO AI LIVELLI WAVELET CHE CATTURANO CONTENUTI FREQUENTISTICI DIVERSI! (i.e., θ+δ, θ e δ)

'''

#PER I LIVELLI WAVELET!

import numpy as np

# Nuovo dizionario per i risultati concatenati
new_all_pt_concat_reconstructions_coupled_exp = {}

# Iteriamo attraverso tutti i soggetti e per ogni condizione
for subject, subject_data in new_subject_level_concatenations_coupled_exp_pt_1_20.items():
    
    for condition, data_labels in subject_data.items():
        
        # Se la condizione non esiste ancora nel dizionario finale, la inizializziamo
        if condition not in new_all_pt_concat_reconstructions_coupled_exp:
            new_all_pt_concat_reconstructions_coupled_exp[condition] = {
                'data': data_labels['data'],
                'labels': data_labels['labels']
            }
        else:
            # Concatenare i dati e le etichette per la condizione
            new_all_pt_concat_reconstructions_coupled_exp[condition]['data'] = np.concatenate(
                (new_all_pt_concat_reconstructions_coupled_exp[condition]['data'], data_labels['data'])
            )
            new_all_pt_concat_reconstructions_coupled_exp[condition]['labels'] = np.concatenate(
                (new_all_pt_concat_reconstructions_coupled_exp[condition]['labels'], data_labels['labels'])
            )

# Verifica dei risultati
#print("Dati concatenati per ciascuna condizione:")
#for condition in new_all_pt_concat_reconstructions_coupled_exp:
#    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_pt_concat_reconstructions_coupled_exp[condition]['data'].shape}, Shape Etichette: {new_all_pt_concat_reconstructions_coupled_exp[condition]['labels'].shape}")
#    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_pt_concat_reconstructions_coupled_exp[condition]['labels'], return_counts = True)}")
#    print()


# Verifica dei risultati
#print("Dati concatenati per ciascuna condizione:")
#for condition in new_all_pt_concat_reconstructions_coupled_exp:
#    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_pt_concat_reconstructions_coupled_exp[condition]['data'].shape}, Shape Etichette: {new_all_pt_concat_reconstructions_coupled_exp[condition]['labels'].shape}")
#    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_pt_concat_reconstructions_coupled_exp[condition]['labels'], return_counts=True)}")
    
#    print(f"\n\033[4mShape delle etichette per ciascun soggetto nella condizione \033[1m{condition}\033[0m:\033[0m")
#    for subject, subject_data in new_subject_level_concatenations_coupled_exp_pt_1_20.items():
#        if condition in subject_data:
#            subject_labels = subject_data[condition]['labels']
#            print(f"- {subject}: {subject_labels.shape}")
#    print()

print('fatto')

In [ ]:
print(new_all_pt_concat_reconstructions_coupled_exp.keys())
print()
print(new_all_pt_concat_reconstructions_coupled_exp['baseline_vs_th_resp'].keys())
print()
print(new_all_pt_concat_reconstructions_coupled_exp['baseline_vs_th_resp']['labels'].shape)
print()
print(np.unique(new_all_pt_concat_reconstructions_coupled_exp['baseline_vs_th_resp']['labels'], return_counts = True))

In [ ]:
print(new_all_pt_concat_reconstructions_coupled_exp['baseline_vs_th_resp'].keys())
print()
print(new_all_pt_concat_reconstructions_coupled_exp['baseline_vs_pt_resp'].keys())
print()
print(new_all_pt_concat_reconstructions_coupled_exp['baseline_vs_shared_resp'].keys())
print()
print(new_all_pt_concat_reconstructions_coupled_exp['th_resp_vs_pt_resp'].keys())
print()
print(new_all_pt_concat_reconstructions_coupled_exp['th_resp_vs_shared_resp'].keys())
print()
print(new_all_pt_concat_reconstructions_coupled_exp['pt_resp_vs_shared_resp'].keys())

In [ ]:
'''ORA, QUELLO CHE INVECE CI SERVE CREARE, INVECE, 

SAREBBE LA VARIABILE CHE CONCATENA FRA TUTTI I SOGGETTI, I DATI E LE LABELS DELLA CHIAVE CHE IDENTIFICA
LA STESSA CONDIZIONE SPERIMENTALE SULLA QUALE STIAMO ITERANDO AL CICLO CORRENTE DEL FOR LOOP

SIA PER I DATI WAVELET, CHE PER I DATI 1-20!!!


Quindi, per ogni condizione sperimentale,
andiamo a concatenare tutti i dati e le etichette relativi a quella condizione,
ma provenienti da tutti i soggetti. 

Ogni condizione sperimentale ha già i dati e le etichette concatenati per ciascun soggetto,
e ora bisogna unire questi dati da tutti i soggetti per ogni condizione.

Immagina la struttura così:

Condizione sperimentale (per esempio, "condizione_1"):
Unire i dati di tutti i soggetti per la condizione "condizione_1".
Unire le etichette di tutti i soggetti per la condizione "condizione_1".


# La tua struttura dati originale 1_20
new_subject_level_concatenations_coupled_exp_th = {
    'subject_1': {
        'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
        'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        '
    'subject_2': {
        'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
        'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        
    subject_3': {
        'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
        'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        
    }
}


ATTENZIONE! SICCOME IO ITERO ANCHE RISPETTO AI LIVELLI DI RICOSTRUZIONE, 
LE CONCATENAZIONI VENGANO FATTE PER 3 VOLTE (1 PER CIASCUN LIVELLO)

MA QUESTO RISULTA OVVIAMENTE ERRATO! 

DI CONSEGUENZA, PER CALCOLARE LE LABELS PER OGNI CONDIZIONE SPERIMENTALE, 

SI FA RIFERIMENTO A     "new_all_th_concat_reconstructions_coupled_exp_1_20"

- SIA PER I LIVELLI WAVELET 
- SIA PER IL "LIVELLO" EEG FILTERED 1-20

QUESTO PERCHÉ OVVIAMENTE LE LABELS NON È CHE SI 'RADDOPPIANO' SOLO PER IL FATTO CHE STO CONSIDERANDO
DIVERSI LIVELLI DI RICOSTRUZIONE, MA È SOLO PER TESTARE LE DIFFERENTI PERFORMANCE DI CLASSIFICAZIONE 
RISPETTO AI LIVELLI WAVELET CHE CATTURANO CONTENUTI FREQUENTISTICI DIVERSI! (i.e., θ+δ, θ e δ)

'''

#PER I EEG FILTERED 1-20 Hz!

import numpy as np

# Nuovo dizionario per i risultati concatenati
new_all_pt_concat_reconstructions_coupled_exp_1_20 = {}

# Iteriamo attraverso tutti i soggetti e per ogni condizione
for subject, subject_data in new_subject_level_concatenations_coupled_exp_pt_1_20.items():
    
    for condition, data_labels in subject_data.items():
        
        # Se la condizione non esiste ancora nel dizionario finale, la inizializziamo
        if condition not in new_all_pt_concat_reconstructions_coupled_exp_1_20:
            new_all_pt_concat_reconstructions_coupled_exp_1_20[condition] = {
                'data': data_labels['data'],
                'labels': data_labels['labels']
            }
        else:
            # Concatenare i dati e le etichette per la condizione
            new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['data'] = np.concatenate(
                (new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['data'], data_labels['data'])
            )
            new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['labels'] = np.concatenate(
                (new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['labels'], data_labels['labels'])
            )


print('Fatto!')
# Verifica dei risultati
#print("Dati concatenati per ciascuna condizione:")
#for condition in new_all_th_concat_reconstructions_coupled_exp_1_20:
#    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['data'].shape}, Shape Etichette: {new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['labels'].shape}")
#    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['labels'], return_counts = True)}")
#    print()


# Verifica dei risultati
#print("Dati concatenati per ciascuna condizione:")
#for condition in new_all_pt_concat_reconstructions_coupled_exp_1_20:
#    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['data'].shape}, Shape Etichette: {new_all_pt_concat_reconstructions_coupled_exp[condition]['labels'].shape}")
#    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_pt_concat_reconstructions_coupled_exp[condition]['labels'], return_counts=True)}")
#    
#    print(f"\n\033[4mShape delle etichette per ciascun soggetto nella condizione \033[1m{condition}\033[0m:\033[0m")
#    for subject, subject_data in new_subject_level_concatenations_coupled_exp_pt_1_20.items():
#        if condition in subject_data:
#            subject_labels = subject_data[condition]['labels']
#            print(f"- {subject}: {subject_labels.shape}")
#    print()


In [ ]:
print(statistics_level_4_pt_fam.keys())
print(statistics_level_4_pt_fam['svm'].keys())
print(statistics_level_4_pt_fam['svm']['baseline_vs_th_resp'].keys())
print(statistics_level_4_pt_fam['svm']['baseline_vs_th_resp']['0-50'].keys())

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **COUPLED EXPERIMENTAL CONDITIONS**

##### **PLOTS DEI TREND DI ACCURATEZZA DI CLASSIFICAZIONE PER OGNI SINGOLO ML CLASSIFIER RISPETTO A TUTTE E 6 LE CONDIZIONI SPERIMENTALI PER LO STESSO LIVELLO WAVELET**

In [ ]:
import pickle

#FAMILIARI

#fam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'


# Caricare l'intero dizionario annidato con pickle
#with open(f'{fam_path}/statistics_level_4_th_fam.pkl', 'rb') as f:
#    statistics_level_4_th_fam = pickle.load(f)
    
# Caricare l'intero dizionario annidato con pickle
#with open(f'{fam_path}/statistics_level_4_pt_fam.pkl', 'rb') as f:
#    statistics_level_4_pt_fam = pickle.load(f)
       

#NON FAMILIARI
#unfam_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE_NF'

# Caricare l'intero dizionario annidato con pickle
#with open(f'{unfam_path}/statistics_level_4_th_unfam.pkl', 'rb') as f:
#    statistics_level_4_th_unfam = pickle.load(f)
    

# Caricare l'intero dizionario annidato con pickle
#with open(f'{unfam_path}/statistics_level_4_pt_unfam.pkl', 'rb') as f:
#    statistics_level_4_pt_unfam = pickle.load(f)
    


In [ ]:
'''
def stampa_media_per_finestra_confronto(svm_stats_1, svm_stats_2):
    """Funzione per stampare la media per ogni finestra in due dizionari di SVM"""
    # Itera sulle chiavi comuni tra i due dizionari (condizioni)
    for condizione in svm_stats_1.keys():
        print(f"\nCondizione: \033[1m{condizione}\033[0m\n")
        
        # Per ogni finestra temporale
        for finestra_temporale in svm_stats_1[condizione].keys():
            # Estrai la media per la finestra per entrambi i gruppi
            media_1 = svm_stats_1[condizione][finestra_temporale]['mean']
            media_2 = svm_stats_2[condizione][finestra_temporale]['mean']
            
            # Stampa la media per la finestra accanto accanto per entrambi i gruppi
            print(f"  Finestra: {finestra_temporale} -> \033[1mMedia TH UNFAM\033[0m: {media_1:.4f} | \033[1mMedia PT UNFAM\033[0m: {media_2:.4f}")
            if media_1 == media_2:
                print('MEDIA UGUALE!')
            else:
                pass
                    
# Confronta i dizionari 'svm' tra i due gruppi
print("Confronto delle medie \033[1mSVM\033[0m:\n")
stampa_media_per_finestra_confronto(statistics_level_4_th_unfam['svm'], statistics_level_4_pt_unfam['svm'])
#stampa_media_per_finestra_confronto(statistics_level_4_th_unfam, statistics_level_4_pt_unfam)
'''

In [ ]:
def stampa_media_per_finestra_confronto_per_classifier(stats_1, stats_2):
    """Funzione per stampare la media per ogni finestra per ogni classifier"""
    
    # Itera su tutti i classifier (es. 'logistic_regression', 'xgboost', 'svm')
    for classifier in stats_1.keys():
        print(f"\nClassifier: \033[1m{classifier}\033[0m")
        
        # Itera sulle chiavi delle condizioni
        for condizione in stats_1[classifier].keys():
            print(f" \nCondizione: \033[1m{condizione}\033[0m")
            
            # Itera su tutte le finestre temporali
            for finestra_temporale in stats_1[classifier][condizione].keys():
                # Estrai la media per la finestra per entrambi i gruppi
                media_1 = stats_1[classifier][condizione][finestra_temporale]['mean']
                media_2 = stats_2[classifier][condizione][finestra_temporale]['mean']
                
                # Stampa la media per la finestra accanto accanto per entrambi i gruppi
                print(f"  Finestra: {finestra_temporale} -> \033[1mMedia TH\033[0m: {media_1:.4f} | \033[1mMedia PT\033[0m: {media_2:.4f}")
                
                if media_1 == media_2:
                    print('MEDIA UGUALE!')
                else:
                    pass
                    
                
# Confronta i dizionari 'svm', 'logistic_regression' e 'xgboost' tra i due gruppi
print("Confronto delle medie per ogni classifier:")
stampa_media_per_finestra_confronto_per_classifier(statistics_level_4_th_fam, statistics_level_4_pt_fam)


In [ ]:
'''PLOTS DEI 6 TREND PER OGNI SINGOLO CLASSIFIER RISPETTO AL LIVELLO DELLA FEATURE WAVELET (4,5,5_detail)

Ecco una versione aggiornata del codice, in cui si va a creare 

Una figura con 2 plots, per ciascun classificatore e ciascun livello di ricostruzione,
mostrando i 6 trend di accuratezza medi di classificazione, 
ciascuno identificante una specifica coppia di condizioni sperimentali. 

Ogni figura include due sottoplot: uno nel dominio delle finestre e uno nel dominio del tempo.

Il codice utilizza colori distintivi per ogni coppia di condizioni sperimentali 
e mantiene la struttura generale di prima, 
aggiungendo la logica per generare i due sottoplot per classificatore e livello.

                                        
                                            CON DOMINIO SOLO DEL TEMPO !!!

'''


import numpy as np
import matplotlib.pyplot as plt
import matplotlib.lines as mlines
import os
import math


# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni


time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)


# Colori per le coppie di condizioni sperimentali
condition_colors = {
    'baseline_vs_th_resp': 'red',
    'baseline_vs_pt_resp': 'blue',
    'baseline_vs_shared_resp': 'green',
    'th_resp_vs_pt_resp': 'orange',
    'th_resp_vs_shared_resp': 'purple',
    'pt_resp_vs_shared_resp': 'deepskyblue'
}

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_level_dict, level_str, save_path):
    
    # Crea la cartella principale 'mean_wavelet_levels' dentro 'patients'
    mean_wavelet_levels_path = os.path.join(save_path, 'mean_wavelet_levels_2_classes', 'patients')
    os.makedirs(mean_wavelet_levels_path, exist_ok=True)
    
    # Crea una lista per le finestre
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Inizializzo le medie per ogni classificatore, separati per condizione
    mean_scores = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
                   for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    ci_low = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
              for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    ci_high = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
               for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
    window_starts_samples = []
    window_ends_samples = []
    window_mid_points_samples = []

    # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
    start_sample = 0

    while start_sample + window_size_samples <= n_samples:
        end_sample = start_sample + window_size_samples
        window_starts_samples.append(start_sample)
        window_ends_samples.append(end_sample)
        window_mid_points_samples.append(start_sample + window_size_samples // 2)
        start_sample += stride_samples

    # Conversione dei punti in millisecondi
    window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
    window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
    window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    # Numero di condizioni sperimentali
    conditions = list(statistics_level_dict['logistic_regression'].keys())
            
    # Itera su tutti i classificatori
    for classifier in ['logistic_regression', 'xgboost', 'svm']:
        
        classier_path = os.path.join(mean_wavelet_levels_path, classifier)
        os.makedirs(classier_path, exist_ok=True)
    
        
        # Impostiamo i sottoplot: uno per le finestre e uno per il dominio del tempo
        
        #OPZIONE 1 
        # Crea una nuova figura per ogni classificatore
        
        #plt.figure(figsize=(10, 14))
        #ax1 = plt.subplot(211)  # Sottoplot per il dominio finestre
        #ax2 = plt.subplot(212)  # Sottoplot per il dominio temporale
        
        #OPZIONE 2
        # Crea una nuova figura per ogni classificatore
        
        plt.figure(figsize=(10, 7))
        #ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
        #ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale
        
        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        print(f"\t\t\t\t\t\tProcessing classifier: \033[1m{classifier}\033[0m")
        
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        
        #prestimulus_added_ax1 = False
        #prestimulus_added_ax2 = False
        
        prestimulus_added_plt = False
        
        
        # Aggiungi i punteggi medi dei classificatori e gli intervalli di confidenza per ogni condizione
        for condition in conditions:
                
            if condition in statistics_level_dict[classifier].keys():
                
                # Itera sulle finestre e sui punti medi simultaneamente
                for window, mid_point in zip(n_windows, window_mid_points_in_ms):

                    # Recupera i dati relativi alla finestra corrente
                    window_data = statistics_level_dict[classifier][condition].get(window, None)
                    
                    if window_data:
                        
                        # Aggiungi i valori di media e CI intervals alle strutture dati che ho creato
                        mean_best_score = window_data['mean']
                        ci_lower = window_data['ci_lower']
                        ci_upper = window_data['ci_upper']
                        
                        # Popolo le strutture con i valori medi e gli intervalli di confidenza
                        mean_scores[classifier][condition].append(mean_best_score)
                        ci_low[classifier][condition].append(ci_lower)
                        ci_high[classifier][condition].append(ci_upper)
                
                '''
                GESTIONE CON 2 SUBPLOTS
                
                # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
                if level_str == '4':
                    ax1.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ+δ Range", fontsize = 18)
                    ax2.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ+δ Range", fontsize = 18)
                    
                elif level_str == '5':
                    ax1.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - δ Range", fontsize = 18)
                    ax2.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - δ Range", fontsize = 18)

                elif level_str == '5_detail':
                    ax1.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ Range", fontsize = 18)
                    ax2.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ Range", fontsize = 18)
                '''
                
                '''
                GESTIONE CON 1 PLOT SOLO
                '''
                
                # Se il livello è 4, 5, o 5_detail, gestisci i titoli per i grafici su ax1 e ax2
                if level_str == '4':
                    plt.title(f"Patients' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ+δ Range", fontsize = 12)
                    
                    
                elif level_str == '5':
                    plt.title(f"Patients' Mean Best Accuracy Score for {classifier} - Level {level_str} - δ Range", fontsize = 12)
                    

                elif level_str == '5_detail':
                    plt.title(f"Patients' Mean Best Accuracy Score for {classifier} - Level {level_str} - Θ Range", fontsize = 12)
                
                
                '''
                PLOTS CON ASSE NEL DOMINIO DELLE FINESTRE (MA ENTRAMBI ASSIEME)
                
                # Aggiungi la linea di prestimolo solo la prima volta
                if not prestimulus_added_ax1:
                    ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
                    prestimulus_added_ax1 = True
                    
                ax1.plot(window_mid_points_in_ms, mean_scores[classifier][condition], 
                         label=f'{condition}', color=condition_colors[condition])
                
                if level_str == '4':
                    ax1.set_ylim(0.55, 0.68)
                
                elif level_str == '5':
                    ax1.set_ylim(0.55, 0.70)
                
                elif level_str == '5_detail':
                    ax1.set_ylim(0.54, 0.68)
                
                # Imposta le etichette principali per il dominio finestre (ax1)
                ax1.set_xticks(tick_positions)
                ax1.set_xticklabels(window_labels)
                
                # Modifica del fontsize dei tick dell'asse x ed y
                ax1.tick_params(axis='x', labelsize=18)
                ax1.tick_params(axis='y', labelsize=18)

                ax1.set_xlabel('Windows (50 samples)', fontweight='bold',fontsize = 20)
                ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)
                  
                
                ax1.legend(prop={'weight': 'bold', 'size': 12},loc='best')
                ax1.grid(True)
                '''
                
    
                '''PLOTS CON ASSE NEL DOMINIO DEL TEMPO (MA ENTRAMBI ASSIEME)
                
                # Aggiungi la linea di prestimolo solo la prima volta
                if not prestimulus_added_ax2:
                    ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
                    prestimulus_added_ax2 = True
                    
        
                ax2.plot(window_mid_points_in_ms, mean_scores[classifier][condition], 
                         label=f'{condition}', color=condition_colors[condition])
                
                if level_str == '4':
                    ax2.set_ylim(0.55, 0.68)
                
                elif level_str == '5':
                    ax2.set_ylim(0.55, 0.70)
                
                elif level_str == '5_detail':
                    ax2.set_ylim(0.54, 0.68)
                
                    
                # Imposta le etichette principali per il dominio temporale (ax2)
                ax2.set_xticks(window_mid_points_in_ms)
                ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])
                
                # Modifica del fontsize dei tick dell'asse x ed y
                ax2.tick_params(axis='x', labelsize=18)
                ax2.tick_params(axis='y', labelsize=18)
        
                ax2.set_xlabel('Time (mms)', fontweight='bold', fontsize = 20)
                ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 20)
                
                ax2.legend(prop={'weight': 'bold', 'size': 13}, loc='best')
                ax2.grid(True)
                '''
                
                # Aggiungi il grafico utilizzando plt
                if not prestimulus_added_plt:
                    plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
                    prestimulus_added_plt = True

                plt.plot(window_mid_points_in_ms, mean_scores[classifier][condition], 
                         label=f'{condition}', color=condition_colors[condition])
                
                # Aggiunta dell'intervallo di confidenza
                plt.fill_between(window_mid_points_in_ms, 
                                 ci_low[classifier][condition], 
                                 ci_high[classifier][condition], 
                                 color=condition_colors[condition], 
                                 alpha=0.1)  # Opacità per visualizzare meglio l'intervallo
                
                if level_str == '4':
                    #plt.ylim(0.55, 0.68)
                    plt.ylim(0.52, 0.70)

                elif level_str == '5':
                    #plt.ylim(0.55, 0.70)
                    plt.ylim(0.52, 0.70)
                    
                elif level_str == '5_detail':
                    #plt.ylim(0.54, 0.68)
                    plt.ylim(0.52, 0.70)
                
                # Imposta le etichette principali per il dominio temporale (ax2)
                plt.xticks(window_mid_points_in_ms)
                #plt.ticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])
                
                # Modifica del fontsize dei tick dell'asse x ed y
                plt.tick_params(axis='x', labelsize=12)
                plt.tick_params(axis='y', labelsize=12)

                # Imposta le etichette principali per il dominio temporale
                plt.xticks(window_mid_points_in_ms, [f'{int(pos)}' for pos in window_mid_points_in_ms], fontsize=12)
                plt.xlabel('Time (mms)', fontweight='bold', fontsize=12)
                plt.ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize=12)

                plt.legend(prop={'weight': 'bold', 'size': 8}, loc='best')
                plt.grid(True)

        #plt.show()
        
        # Salva il plot per ogni classificatore
        filename = f'mean_best_scores_{classifier}_level_{level_str}_all_paired_conditions_time_domain_and_conf_interval.png' 
        save_file_path = os.path.join(save_path, 'mean_wavelet_levels_2_classes', 'patients', classier_path, filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[0m\n')

# Esegui per ciascun livello
save_path = f'/home/stefano/Interrogait/{familiar_path}/all_classifiers_plots/EEG_2_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/'

plot_mean_best_scores_for_window(statistics_level_4_pt_fam, '4', save_path)
plot_mean_best_scores_for_window(statistics_level_5_pt_fam, '5', save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail_pt_fam, '5_detail', save_path)


##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE PER IL LEVEL 4 E 5 DA COEFF APPROX + LEVEL 5 COEFF DETAIL DELLE RICOSTRUZIONI** - **COUPLED EXPERIMENTAL CONDITIONS**

##### **PLOTS DEI TREND DI ACCURATEZZA DI CLASSIFICAZIONE PER OGNI SINGOLO ML CLASSIFIER RISPETTO AD OGNI SINGOLA COPPIA DI CONDIZIONE SPERIMENTALE TESTATA PER TUTTE E 3 LIVELLI WAVELET**

Qui le **figure** sono divise in modo che ****ogni condizione sperimentale****, abbia plottati ****i trend di accuratezza di classificazione****, per la **stessa condizione sperimentale**, per ognuno dei ****3 livelli di ricostruzione del segnale****... 

In questo caso, per maggior visibilità grafica, si impone che, il trend di classificazione tramite lo stesso classificatore per la stessa condizione sperimentale (che ha uno stesso colore) abbia una stile della linea diverso per ogni feature wavelet:

- Livello **approx 4**: **Θ+δ band**
- Livello **approx 5**: **δ band**
- Livello **detail 5**: **Θ band**

In questo modo, si osserva come cambia il rate di discriminabilità rispetto all'uso di una certa wavelet per un certo classificatore, per una determinata condizione sperimentale...



In [ ]:
print(statistics_level_4_pt_fam['svm']['baseline_vs_th_resp']['0-50'].keys())
print(statistics_level_4_pt_fam['svm']['baseline_vs_th_resp']['0-50']['mean'])
print(statistics_level_4_th_fam['svm']['baseline_vs_th_resp']['0-50']['mean'])

In [ ]:
'''  PLOTS DEI 3 TREND PER OGNI SINGOLO CLASSIFIER PER OGNI CONDIZIONE SPERIMENTALE
RISPETTO AL LIVELLO DELLA FEATURE WAVELET (4,5,5_detail)

Ecco una versione aggiornata del codice, in cui si andrebbe a creare 

Una figura con 2 plots, per ciascun condizione sperimentale e classifier,
mostrando i 3 trend di accuratezza medi di classificazione, 
rispetto alla stessa condizione sperimentale,

rispetto all'uso delle 3 feature wavelet usate

Ogni figura include due sottoplot: uno nel dominio delle finestre e uno nel dominio del tempo.

Il codice utilizza ora invece distintivi per ogni coppia di condizioni sperimentali 
e mantiene la struttura generale di prima, 
aggiungendo la logica per generare i due sottoplot per classificatore e livello.


                                        CON DOMINIO SOLO DEL TEMPO !!!

'''

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.lines as mlines
import os
import math


# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni


time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)


# Colori per le coppie di condizioni sperimentali
condition_colors = {
    'baseline_vs_th_resp': 'red',
    'baseline_vs_pt_resp': 'blue',
    'baseline_vs_shared_resp': 'green',
    'th_resp_vs_pt_resp': 'orange',
    'th_resp_vs_shared_resp': 'purple',
    'pt_resp_vs_shared_resp': 'deepskyblue'
}

familiar_path = 'New_Plots_Sliding_Estimator_MNE'

def plot_mean_best_scores_for_window(statistics_level_dict, level_str, save_path):
    
    # Crea la cartella principale 'mean_wavelet_levels' dentro 'patients'
    mean_wavelet_levels_path = os.path.join(save_path, 'mean_wavelet_levels_2_classes', 'patients')
    os.makedirs(mean_wavelet_levels_path, exist_ok=True)
    
    # Crea una lista per le finestre
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    # Struttura dati per incorporare statistiche di ogni feature wavelet
    wavelet_levels = {
        'Θ+δ band': statistics_level_4_pt_fam, # Theta + Delta feature
        'δ band': statistics_level_5_pt_fam, # Delta feature
        'Θ band': statistics_level_5_detail_pt_fam # Theta feature
    }

    # Stili di linea per ogni feature
    wavelet_styles = {
        'Θ+δ band': '-',  # Stile tratteggiato per Theta
        'δ band': '--',  # Linea continua per Delta
        'Θ band': ':',  # Linea puntinata per Theta + Delta
    }
    
    
    # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
    window_starts_samples = []
    window_ends_samples = []
    window_mid_points_samples = []

    # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
    start_sample = 0

    while start_sample + window_size_samples <= n_samples:
        end_sample = start_sample + window_size_samples
        window_starts_samples.append(start_sample)
        window_ends_samples.append(end_sample)
        window_mid_points_samples.append(start_sample + window_size_samples // 2)
        start_sample += stride_samples

    # Conversione dei punti in millisecondi
    window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
    window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
    window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    
    # Numero di condizioni sperimentali
    conditions = list(statistics_level_dict['logistic_regression'].keys())
    
    for condition in conditions:
        
        print(f"\t\t\t\tProcessing condition: \033[1m{condition}\033[0m")
        
        # Variabile per controllare se la linea del prestimolo è già stata aggiunta alla legenda
        
        #prestimulus_added_ax1 = False
        #prestimulus_added_ax2 = False
        
        prestimulus_added_plt = False
        
        for classifier in ['logistic_regression', 'xgboost', 'svm']:

            # Crea la sotto-cartella principale per il classifier
            classifier_path = os.path.join(save_path, 'mean_wavelet_levels_2_classes', 'patients', classifier)
            os.makedirs(classifier_path, exist_ok=True)
            
            wavelet_comparisons_path = os.path.join (classifier_path, 'wavelets_comparisons')
            os.makedirs(wavelet_comparisons_path, exist_ok=True)
            
            # Impostiamo i sottoplot: uno per le finestre e uno per il dominio del tempo
        
            #OPZIONE 1 
            # Crea una nuova figura per ogni classificatore

            #plt.figure(figsize=(10, 14))
            #ax1 = plt.subplot(211)  # Sottoplot per il dominio finestre
            #ax2 = plt.subplot(212)  # Sottoplot per il dominio temporale

            #OPZIONE 2
            # Crea una nuova figura per ogni classificatore

            #plt.figure(figsize=(26, 10))
            #ax1 = plt.subplot(121)  # Sottoplot per il dominio finestre
            #ax2 = plt.subplot(122)  # Sottoplot per il dominio temporale
        
            plt.figure(figsize=(10, 7))


            # Creiamo le etichette per le finestre
            window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
            tick_positions = window_mid_points_in_ms

            if condition in statistics_level_dict[classifier].keys():
                
                mean_scores_dict = {wavelet_name: [] for wavelet_name in wavelet_levels}
                ci_lower_dict = {wavelet_name: [] for wavelet_name in wavelet_levels}
                ci_upper_dict = {wavelet_name: [] for wavelet_name in wavelet_levels}
                
                # Itera su tutte le wavelet (theta, delta, theta+delta)
                for wavelet_name, wavelet_data in wavelet_levels.items():
                    
                    if condition in wavelet_data[classifier]:
                        for window in n_windows:
                            window_data = wavelet_data[classifier][condition].get(window, None)

                            if window_data:
                                mean_scores_dict[wavelet_name].append(window_data['mean'])
                                ci_lower_dict[wavelet_name].append(window_data['ci_lower'])
                                ci_upper_dict[wavelet_name].append(window_data['ci_upper'])
                    
                    '''
                    
                    PLOTS CON ASSE NEL DOMINIO DELLE FINESTRE (MA ENTRAMBI ASSIEME)
                    
                    # Aggiungi la linea di prestimolo solo la prima volta
                    if not prestimulus_added_ax1:
                        ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
                        prestimulus_added_ax1 = True
                    
                    # PLOT DEI TREND DI CLASSIFICAZIONE NEL DOMINIO DELLE FINESTRE E TEMPO
                    
                    
                    # Plotta per ogni wavelet separatamente
                    ax1.plot(window_mid_points_in_ms, mean_scores_dict[wavelet_name], 
                             label=f'{wavelet_name} - {classifier}', color=condition_colors[condition], linestyle=wavelet_styles[wavelet_name])
                    
                    if condition == 'baseline_vs_th_resp': 
                        ax1.set_ylim(0.58, 0.69)
                        
                    elif condition == 'baseline_vs_pt_resp':
                        ax1.set_ylim(0.58, 0.67)
                        
                    elif condition =='baseline_vs_shared_resp':
                        ax1.set_ylim(0.54, 0.66)
                        
                    elif condition =='th_resp_vs_pt_resp':
                        ax1.set_ylim(0.55, 0.65)
                        
                    elif condition =='th_resp_vs_shared_resp':
                        ax1.set_ylim(0.56, 0.67)
                        
                    elif condition =='pt_resp_vs_shared_resp':
                        ax1.set_ylim(0.58, 0.66)
                        
                    # Imposta le etichette principali per il dominio finestre (ax1)
                    ax1.set_xticks(tick_positions)
                    ax1.set_xticklabels(window_labels)
                    
                    # Modifica del fontsize dei tick dell'asse x ed y
                    ax1.tick_params(axis='x', labelsize=16)
                    ax1.tick_params(axis='y', labelsize=16)
                    
                    
                    '''
                    
                    '''
                    PLOTS CON ASSE NEL DOMINIO DELLE TEMPO (MA ENTRAMBI ASSIEME)
                    
                    # Aggiungi la linea di prestimolo solo la prima volta
                    if not prestimulus_added_ax2:
                        ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
                        prestimulus_added_ax2 = True

                    ax2.plot(window_mid_points_in_ms, mean_scores_dict[wavelet_name], 
                             label=f'{wavelet_name} - {classifier}', color=condition_colors[condition], linestyle=wavelet_styles[wavelet_name])
                    
                    if condition == 'baseline_vs_th_resp': 
                        ax2.set_ylim(0.58, 0.69)
                        
                    elif condition == 'baseline_vs_pt_resp': 
                        ax2.set_ylim(0.58, 0.67)
                        
                    elif condition =='baseline_vs_shared_resp':
                        ax2.set_ylim(0.54, 0.66)
                        
                    elif condition =='th_resp_vs_pt_resp': 
                        ax2.set_ylim(0.55, 0.65)
                        
                    elif condition =='th_resp_vs_shared_resp': 
                        ax2.set_ylim(0.56, 0.67)
                        
                    elif condition =='pt_resp_vs_shared_resp': 
                        ax2.set_ylim(0.58, 0.66)
                        
                        
                    # Imposta le etichette principali per il dominio temporale (ax2)
                    ax2.set_xticks(window_mid_points_in_ms)
                    ax2.set_xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])
                    
                    # Modifica del fontsize dei tick dell'asse x ed y
                    ax2.tick_params(axis='x', labelsize=16)
                    ax2.tick_params(axis='y', labelsize=16)
                    
                    '''
                    
                    # Aggiungi la linea di prestimolo solo la prima volta
                    if not prestimulus_added_plt:
                        plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
                        prestimulus_added_plt = True

                    plt.plot(window_mid_points_in_ms, mean_scores_dict[wavelet_name], 
                             label=f'{wavelet_name} - {classifier}', color=condition_colors[condition], linestyle=wavelet_styles[wavelet_name])
                    
                    if condition == 'baseline_vs_th_resp': 
                        plt.ylim(0.58, 0.69)
                        
                    elif condition == 'baseline_vs_pt_resp': 
                        plt.ylim(0.58, 0.67)
                        
                    elif condition =='baseline_vs_shared_resp':
                        plt.ylim(0.54, 0.66)
                        
                    elif condition =='th_resp_vs_pt_resp': 
                        plt.ylim(0.55, 0.65)
                        
                    elif condition =='th_resp_vs_shared_resp': 
                        plt.ylim(0.56, 0.67)
                        
                    elif condition =='pt_resp_vs_shared_resp': 
                        plt.ylim(0.58, 0.66)
                        
                        
                    # Imposta le etichette principali per il dominio temporale (ax2)
                    plt.xticks(window_mid_points_in_ms)
                    #plt.xticklabels([f'{int(pos)}' for pos in window_mid_points_in_ms])
                    
                    # Modifica del fontsize dei tick dell'asse x ed y
                    plt.tick_params(axis='x', labelsize=12)
                    plt.tick_params(axis='y', labelsize=12)
                    
                    
                '''
                GESTIONE 2 SUBPLOTS
                
                # Aggiungi il titolo e la legenda
                ax1.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} in {condition} - All Wavelets", fontsize = 14)
                
                ax2.set_title(f"Therapists' Mean Best Accuracy Score for {classifier} in {condition} - All Wavelets", fontsize = 14)
                
                ax1.set_xlabel('Windows (50 samples)', fontweight='bold', fontsize = 18)
                ax1.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 18)
                ax2.set_xlabel('Time (ms)', fontweight='bold', fontsize = 18)
                ax2.set_ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 18)
                
                ax1.legend(prop={'weight': 'bold', 'size': 12}, loc='best')
                ax2.legend(prop={'weight': 'bold', 'size': 12}, loc='best')

                ax1.grid(True)
                ax2.grid(True)

                # Linea del prestimolo
                ax1.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
                ax2.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 ms)')
                
                '''
                # Aggiungi il titolo e la legenda
                plt.title(f"Patients' Mean Best Accuracy Score for {classifier} in {condition} - All Wavelets", fontsize = 12)
                
                plt.xlabel('Time (ms)', fontweight='bold', fontsize = 12)
                plt.ylabel('Mean Best Accuracy Score', fontweight='bold', fontsize = 12)
                
                plt.legend(prop={'weight': 'bold', 'size': 9}, loc='best')
                

                plt.grid(True)

                # Linea del prestimolo
                plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 ms)')
                
                
            #plt.show()

            # Salva il plot nel percorso specificato
            filename = f'mean_best_scores_{classifier}_all_wavelets_levels_{condition}_time_domain_and_conf_interval.png' 
            save_file_path = os.path.join(save_path, wavelet_comparisons_path, filename)
            plt.savefig(save_file_path, bbox_inches='tight')
            plt.close()
            print(f'Plot salvato in: \n\033[1m{save_file_path}\033[0m\n')

# Chiamata delle funzioni con i dati
save_path = f'/home/stefano/Interrogait/{familiar_path}/all_classifiers_plots/EEG_2_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/'

plot_mean_best_scores_for_window(statistics_level_4_pt_fam, '4', save_path)
plot_mean_best_scores_for_window(statistics_level_5_pt_fam, '5', save_path)
plot_mean_best_scores_for_window(statistics_level_5_detail_pt_fam, '5_detail', save_path)

##### **ALL SINGLE Patients (PT01-PT20) CODE PER ESTRAZIONE BEST PERFORMANCES SALVATE EEG FILTERED 1-20 Hz DEI RELATIVI MODELLI (i.e., LOGISTIC REGRESSION, XGBOOST e SVM) PER LA RELATIVA FINESTRA TESTATA**

In [ ]:
import os
from collections import OrderedDict

def process_txt_files(base_path, classifiers, n_windows):
    
    # Dizionario per EEG filtered 1-20 Hz
    best_scores_filtered_1_20_all_classifiers_pt_coupled_exp = {}

    # Condizioni sperimentali
    conditions = [
        "baseline_vs_th_resp",
        "baseline_vs_pt_resp",
        "baseline_vs_shared_resp",
        "th_resp_vs_shared_resp",
        "pt_resp_vs_shared_resp",
        "th_resp_vs_pt_resp"
    ]

    # Itera attraverso i classificatori (logistic_regression, xgboost, svm)
    for classifier in classifiers:
        classifier_path = os.path.join(
            base_path, classifier, 
            "EEG_2_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/single_patient_optimized_params_coupled_exp_cond_1_20"
        )
        
        # Controlla se il percorso esiste
        if not os.path.exists(classifier_path):
            print(f"Path not found: {classifier_path}")
            continue

        # Itera attraverso i file nella directory
        for file_name in os.listdir(classifier_path):
            if file_name.endswith(".txt"):
                file_path = os.path.join(classifier_path, file_name)

                # Determina se il file è filtrato
                if "_level_filtered_1_20" not in file_name:
                    continue  # Salta il file se non contiene la stringa desiderata

                # Estrai il soggetto
                subject = None
                if "pt_" in file_name:
                    try:
                        subject = file_name.split("pt_")[1].split("_")[0]
                        subject = int(subject)
                        subject_key = f"pt_{subject}"
                    except (IndexError, ValueError):
                        print(f"Errore nel file name: {file_name}")
                        continue
                
                # Estrai la condizione sperimentale
                condition = None
                for cond in conditions:
                    if cond in file_name:
                        condition = cond
                        break
                if not condition:
                    print(f"Nessuna condizione valida trovata per il file: {file_name}")
                    continue

                # Crea la struttura del dizionario se non esiste
                if subject_key not in best_scores_filtered_1_20_all_classifiers_pt_coupled_exp:
                    best_scores_filtered_1_20_all_classifiers_pt_coupled_exp[subject_key] = {}
                if classifier not in best_scores_filtered_1_20_all_classifiers_pt_coupled_exp[subject_key]:
                    best_scores_filtered_1_20_all_classifiers_pt_coupled_exp[subject_key][classifier] = {}
                if condition not in best_scores_filtered_1_20_all_classifiers_pt_coupled_exp[subject_key][classifier]:
                    best_scores_filtered_1_20_all_classifiers_pt_coupled_exp[subject_key][classifier][condition] = {}

                # Leggi il file .txt
                with open(file_path, 'r') as f:
                    lines = f.readlines()

                    # Cerca la riga che inizia con "Best Score for Window" e il valore float
                    for line in lines:
                        for window in n_windows:
                            if window not in best_scores_filtered_1_20_all_classifiers_pt_coupled_exp[subject_key][classifier][condition]:
                                best_scores_filtered_1_20_all_classifiers_pt_coupled_exp[subject_key][classifier][condition][window] = {}
                            if f"Best Score for Window {window}:" in line:
                                try:
                                    score = float(line.split(":")[1].strip())
                                    best_scores_filtered_1_20_all_classifiers_pt_coupled_exp[subject_key][classifier][condition][window] = score
                                except ValueError:
                                    print(f"Errore durante l'estrazione del punteggio nel file: {file_path}")
                                break
    
    #Ordina le chiavi del dizionario per numero di soggetto
    best_scores_filtered_1_20_all_classifiers_pt_coupled_exp = OrderedDict(
        sorted(best_scores_filtered_1_20_all_classifiers_pt_coupled_exp.items(), key=lambda x: int(x[0].split("_")[1]))
    )


    return best_scores_filtered_1_20_all_classifiers_pt_coupled_exp

# Configurazione dei parametri
base_path = "/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE"
classifiers = ["logistic_regression", "xgboost", "svm"]
n_windows = [f"{i}-{i+50}" for i in range(0, 251, 25)]

# Chiamata della funzione
best_scores_filtered_1_20_all_classifiers_pt_coupled_exp = process_txt_files(base_path, classifiers, n_windows)

# Output dei risultati
print("\033[1mbest_scores_filtered_1_20_all_classifiers_pt_coupled_exp.keys()\033[0m:", best_scores_filtered_1_20_all_classifiers_pt_coupled_exp.keys())


In [ ]:
print(best_scores_filtered_1_20_all_classifiers_pt_coupled_exp.keys())
print()
print(best_scores_filtered_1_20_all_classifiers_pt_coupled_exp['pt_1'].keys())
print()
print(best_scores_filtered_1_20_all_classifiers_pt_coupled_exp['pt_1']['xgboost'].keys())
print()
print(best_scores_filtered_1_20_all_classifiers_pt_coupled_exp['pt_1']['xgboost']['baseline_vs_th_resp'].keys())
print()
print(best_scores_filtered_1_20_all_classifiers_pt_coupled_exp['pt_1']['xgboost']['baseline_vs_th_resp']['0-50'])

In [ ]:
#print(best_scores_level_4_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])
#print()
#print(best_scores_level_5_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])
#print()
#print(best_scores_level_5_detail_th_all_classifiers_coupled_exp['th_1']['xgboost']['baseline_vs_th_resp']['0-50'])

In [ ]:
'''CALCOLO MEDIA, DEV STANDARD E INTERVALLO DI CONFIDENZA PER OGNI CLASSIFIER - NEW VERSION


Cosa fa il codice:
Funzione calculate_mean_and_confidence_interval:

Calcola la media e l'intervallo di confidenza per ogni finestra per ogni confronto 
(per esempio, baseline_vs_th_resp, th_resp_vs_pt_resp, etc.) e classificatore.

Raggruppa i risultati per confronto e finestra temporale.
Calcolo delle statistiche:

Per ciascun livello di ricostruzione (4, 5, 5 dettagliato), la funzione calcola le statistiche per ogni classificatore.
Usa il dizionario con i punteggi migliori (best_scores_level_4_th_all_classifiers_coupled_exp, etc.).

Stampa dei risultati:

La funzione print_bold_statistics stampa i risultati per ogni classificatore, 
confronto e finestra con la media e l'intervallo di confidenza.

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 
Filtra i dati:

Per un classificatore specifico (ad esempio logistic_regression, xgboost, svm).
Per una condizione sperimentale specifica (ad esempio baseline_vs_th_resp).
Per una finestra temporale specifica (ad esempio 0-50).
Raccoglie i Best Score di tutti i soggetti:

Esamina i punteggi per la stessa finestra temporale.
Include solo i soggetti che hanno un punteggio per quel classificatore, quella condizione e quella finestra.
Calcola la statistica:

Media dei punteggi raccolti.
Deviazione standard.
Intervallo di confidenza (CI) al livello di confidenza desiderato (default: 95%), utilizzando la distribuzione t di Student.


Il risultato finale sarà un dizionario annidato, organizzato secondo i seguenti livelli:

Classificatore (ad esempio: logistic_regression, xgboost, svm).
Condizione sperimentale (ad esempio: baseline_vs_th_resp, th_resp_vs_pt_resp).
Finestra temporale (ad esempio: 0-50, 25-75).
Statistiche:
mean: la media dei punteggi.
ci_lower: il limite inferiore dell'intervallo di confidenza.
ci_upper: il limite superiore dell'intervallo di confidenza.

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 
STRUTTURA RISULTANTE

{
    "logistic_regression": {
        "baseline_vs_th_resp": {
            "0-50": {"mean": 0.82, "ci_lower": 0.78, "ci_upper": 0.86},
            "25-75": {"mean": 0.85, "ci_lower": 0.81, "ci_upper": 0.89},
            "50-100": {"mean": 0.80, "ci_lower": 0.76, "ci_upper": 0.84},
            ...
        },
        "th_resp_vs_pt_resp": {
            "0-50": {"mean": 0.75, "ci_lower": 0.70, "ci_upper": 0.80},
            "25-75": {"mean": 0.78, "ci_lower": 0.73, "ci_upper": 0.83},
            ...
        },
        ...
    },
    "xgboost": {
        "baseline_vs_th_resp": {
            "0-50": {"mean": 0.88, "ci_lower": 0.84, "ci_upper": 0.92},
            "25-75": {"mean": 0.87, "ci_lower": 0.83, "ci_upper": 0.91},
            ...
        },
        ...
    },
    "svm": {
        ...
    }
}

----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- ----- 

'''

import numpy as np
import scipy.stats as stats

# Definizione delle finestre temporali
n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
             "150-200", "175-225", "200-250", "225-275", "250-300"]

def calculate_mean_and_confidence_interval(best_scores, classifier, windows, comparisons, confidence_level=0.95):
    """
    Calcola la media e l'intervallo di confidenza per ogni finestra e condizione sperimentale 
    per un classificatore specifico e raccoglie i risultati in un dizionario.
    """
    results = {}

    for comparison in comparisons:
        comparison_results = {}  # Risultati per un confronto specifico

        for window in windows:
            # Raccogli tutti i best scores per questa finestra da tutti i soggetti per il classificatore specificato
            scores = [subject_scores[classifier][comparison][window] 
                      for subject_scores in best_scores.values() 
                      if comparison in subject_scores[classifier] and window in subject_scores[classifier][comparison]]
            
            if scores:  # Se ci sono punteggi
                # Calcola la media
                mean_score = np.mean(scores)
                
                # Calcola la deviazione standard
                std_dev = np.std(scores, ddof=1)
                
                # Numero di soggetti
                n = len(scores)
                
                # Calcola l'intervallo di confidenza
                confidence_interval = stats.t.interval(confidence_level, df=n-1, loc=mean_score, scale=std_dev/np.sqrt(n))
                
                # Salva i risultati per la finestra specifica e il confronto
                comparison_results[window] = {
                    'mean': mean_score,
                    'ci_lower': confidence_interval[0],
                    'ci_upper': confidence_interval[1]
                }
        
        # Salva i risultati per il confronto
        results[comparison] = comparison_results

    return results


# Classificatori e confronti da usare
classifiers = ["logistic_regression", "xgboost", "svm"]
comparisons = ['baseline_vs_th_resp', 'baseline_vs_pt_resp', 'baseline_vs_shared_resp', 
               'th_resp_vs_pt_resp', 'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp']

# Calcolare le statistiche per ciascun livello
statistics_level_1_20 = {
    classifier: calculate_mean_and_confidence_interval(best_scores_filtered_1_20_all_classifiers_pt_coupled_exp, classifier, n_windows, comparisons)
    for classifier in classifiers
}


# Funzione per stampare i risultati con i classificatori in grassetto
def print_bold_statistics(statistics):
    for classifier in statistics:
        print(f"\n\033[1m{classifier}\033[0m\n")  # Stampa il nome del classificatore in grassetto
        for comparison in statistics[classifier]:
            print(f"  \n\033[1m{comparison}\033[0m")  # Stampa il confronto in grassetto
            for window, stats in statistics[classifier][comparison].items():
                print(f"    {window}: Mean = {stats['mean']:.2f}, CI Lower = {stats['ci_lower']:.2f}, CI Upper = {stats['ci_upper']:.2f}")

# Stampa i risultati per ciascun livello
print("\t\t\tRisultati per il \033[1mlivello EEG 1-20Hz\033[0m:")
print_bold_statistics(statistics_level_1_20)

In [ ]:
type(statistics_level_1_20)

In [ ]:
!pwd

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE

In [ ]:
print(statistics_level_1_20.keys())
print()
print(statistics_level_1_20['svm'].keys())
print()
print(statistics_level_1_20['svm']['baseline_vs_th_resp'].keys())
print()
print(statistics_level_1_20['svm']['baseline_vs_th_resp']['0-50'].keys())

In [ ]:
'''               
                        DA QUI IN GIU' BISOGNA UN ATTIMO RAGIONARE! 
    
      DATO CHE IO ORA DOVREI ITERARE RISPETTO A TUTTE LE CONCATENAZIONI MEDIE DI 
      
      OGNI COPPIA DI CONDIZIONI SPERIMETALI CONFRONTATE A COPPIE OSSIA
      
      1) BASELINE_VS_TH_RESP
      2) BASELINE_VS_PT_RESP
      3) BASELINE_VS_SHARED_RESP
      
      4) TH_VS_PT_RESP
      5) TH_VS_SHARED_RESP
      6) PT_RESP_VS_SHARED_RESP
      
      
      ORA, IO HO QUESTE STRUTTURE DATI???
      
      
'''

In [ ]:
#cd ..

In [ ]:
#cd New_Plots_Sliding_Estimator_MNE/

In [ ]:
!pwd

In [ ]:
'''NEW --> cd '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE'''


''' QUESTA VARIABILE NON MI INTERESSA, DATO CHE CONTIENE 
        I DATI CONCATENATI SI', DEL SINGOLO SOGGETTO (CHE MI INTERESSA!),
                    MA PER TUTTE E 4 LE CONDIZIONI SPERIMENTALI INSIEME, OSSIA:
                    
                    1) BASELINE
                    2) TH_RESP
                    3) PT_RESP
                    4) SHARED_RESP
                    
                    ED INVECE A ME INTERESSA PRENDERE
                    I DATI DELLE COPPIE DI CONDIZIONI SPERIMENTALI DEL SINGOLO SOGGETTO!
                    
                    OSSIA
                    
                      1) BASELINE_VS_TH_RESP
                      2) BASELINE_VS_PT_RESP
                      3) BASELINE_VS_SHARED_RESP

                      4) TH_VS_PT_RESP
                      5) TH_VS_SHARED_RESP
                      6) PT_RESP_VS_SHARED_RESP
      
                    
'''    

import pickle

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_pt = pickle.load(f)

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_th'''

print(new_subject_level_concatenations_pt.keys())
print()
print(new_subject_level_concatenations_pt['pt_1'].keys())
print()
print(new_subject_level_concatenations_pt['pt_1']['theta'].shape)

In [ ]:
'''ANCHE QUESTA NON MI INTERESSA, DATO CHE CONTIENE I DATI CONCATENATI, DI TUTTI I SOGGETTI, 
PER TUTTE E 4 LE CONDIZIONI SPERIMENTALI!'''

# Caricare l'intero dizionario annidato con pickle
with open('new_all_pt_concat_reconstructions.pkl', 'rb') as f:
    new_all_pt_concat_reconstructions = pickle.load(f)  

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_all_th_concat_reconstructions'''

print(new_all_pt_concat_reconstructions.keys())
print()
print(new_all_pt_concat_reconstructions['all_pt_fourth_labels'].shape)

In [ ]:
'''QUESTA, INVECE, POTREBBE DIVENTARE LA VARIABILE DI PARTENZA CHE CI INTERESSA,

DATO CHE CONTIENE I DATI CONCATENATI PER OGNI SOGGETTO,

RISPETTO ALLA COPPIA DI CONDIZIONI SPERIMENTALI CHE STIAMO CONFRONTANDO!!!
'''

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt = pickle.load(f)  


In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_coupled_exp_th'''

print(new_subject_level_concatenations_coupled_exp_pt.keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt['pt_1'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_th_resp']['data'].shape)
print()
print(np.unique(new_subject_level_concatenations_coupled_exp_pt['pt_1']['theta']['baseline_vs_pt_resp']['labels'], return_counts = True))

In [ ]:
'''QUESTA, INVECE, POTREBBE DIVENTARE LA VARIABILE DI PARTENZA CHE CI INTERESSA,

DATO CHE CONTIENE I DATI CONCATENATI PER OGNI SOGGETTO,

RISPETTO ALLA COPPIA DI CONDIZIONI SPERIMENTALI CHE STIAMO CONFRONTANDO!!!
'''

# Caricare l'intero dizionario annidato con pickle
with open('new_subject_level_concatenations_coupled_exp_pt_1_20.pkl', 'rb') as f:
    new_subject_level_concatenations_coupled_exp_pt_1_20 = pickle.load(f)  

In [ ]:
'''ESEMPIO PER VISUALIZZARE I DATI DENTRO  --> new_subject_level_concatenations_coupled_exp_th'''

print(new_subject_level_concatenations_coupled_exp_pt_1_20.keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp'].keys())
print()
print(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp']['data'].shape)
print()
print(np.unique(new_subject_level_concatenations_coupled_exp_pt_1_20['pt_1']['baseline_vs_th_resp']['labels'], return_counts = True))

In [ ]:
'''ORA, QUELLO CHE INVECE CI SERVE CREARE, INVECE, 

SAREBBE LA VARIABILE CHE CONCATENA FRA TUTTI I SOGGETTI, I DATI E LE LABELS DELLA CHIAVE CHE IDENTIFICA
LA STESSA CONDIZIONE SPERIMENTALE SULLA QUALE STIAMO ITERANDO AL CICLO CORRENTE DEL FOR LOOP

SIA PER I DATI WAVELET, CHE PER I DATI 1-20!!!


Quindi, per ogni condizione sperimentale,
andiamo a concatenare tutti i dati e le etichette relativi a quella condizione,
ma provenienti da tutti i soggetti. 

Ogni condizione sperimentale ha già i dati e le etichette concatenati per ciascun soggetto,
e ora bisogna unire questi dati da tutti i soggetti per ogni condizione.

Immagina la struttura così:

Condizione sperimentale (per esempio, "condizione_1"):
Unire i dati di tutti i soggetti per la condizione "condizione_1".
Unire le etichette di tutti i soggetti per la condizione "condizione_1".


# La tua struttura dati originale
new_subject_level_concatenations_coupled_exp_th = {
    'subject_1': {
        'theta': {
            'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
            'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        'delta': {
            'condition_1': {'data': np.array([7, 8, 9]), 'labels': np.array([1, 1, 0])},
            'condition_2': {'data': np.array([10, 11, 12]), 'labels': np.array([0, 0, 1])}
        }
    },
    'subject_2': {
        'theta': {
            'condition_1': {'data': np.array([13, 14, 15]), 'labels': np.array([0, 1, 1])},
            'condition_2': {'data': np.array([16, 17, 18]), 'labels': np.array([1, 1, 0])}
        },
        'delta': {
            'condition_1': {'data': np.array([19, 20, 21]), 'labels': np.array([0, 0, 1])},
            'condition_2': {'data': np.array([22, 23, 24]), 'labels': np.array([1, 0, 1])}
        }
    }
}


ATTENZIONE! SICCOME IO ITERO ANCHE RISPETTO AI LIVELLI DI RICOSTRUZIONE, 
LE CONCATENAZIONI VENGANO FATTE PER 3 VOLTE (1 PER CIASCUN LIVELLO)

MA QUESTO RISULTA OVVIAMENTE ERRATO! 

DI CONSEGUENZA, PER CALCOLARE LE LABELS PER OGNI CONDIZIONE SPERIMENTALE, 

SI FA RIFERIMENTO A     "new_all_th_concat_reconstructions_coupled_exp_1_20"

- SIA PER I LIVELLI WAVELET 
- SIA PER IL "LIVELLO" EEG FILTERED 1-20

QUESTO PERCHÉ OVVIAMENTE LE LABELS NON È CHE SI 'RADDOPPIANO' SOLO PER IL FATTO CHE STO CONSIDERANDO
DIVERSI LIVELLI DI RICOSTRUZIONE, MA È SOLO PER TESTARE LE DIFFERENTI PERFORMANCE DI CLASSIFICAZIONE 
RISPETTO AI LIVELLI WAVELET CHE CATTURANO CONTENUTI FREQUENTISTICI DIVERSI! (i.e., θ+δ, θ e δ)

'''

#PER I LIVELLI WAVELET!

import numpy as np

# Nuovo dizionario per i risultati concatenati
new_all_th_concat_reconstructions_coupled_exp = {}

# Iteriamo attraverso tutti i soggetti e per ogni condizione
for subject, subject_data in new_subject_level_concatenations_coupled_exp_th_1_20.items():
    
    for condition, data_labels in subject_data.items():
        
        # Se la condizione non esiste ancora nel dizionario finale, la inizializziamo
        if condition not in new_all_th_concat_reconstructions_coupled_exp:
            new_all_th_concat_reconstructions_coupled_exp[condition] = {
                'data': data_labels['data'],
                'labels': data_labels['labels']
            }
        else:
            # Concatenare i dati e le etichette per la condizione
            new_all_th_concat_reconstructions_coupled_exp[condition]['data'] = np.concatenate(
                (new_all_th_concat_reconstructions_coupled_exp[condition]['data'], data_labels['data'])
            )
            new_all_th_concat_reconstructions_coupled_exp[condition]['labels'] = np.concatenate(
                (new_all_th_concat_reconstructions_coupled_exp[condition]['labels'], data_labels['labels'])
            )

# Verifica dei risultati
print("Dati concatenati per ciascuna condizione:")
for condition in new_all_th_concat_reconstructions_coupled_exp:
    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_th_concat_reconstructions_coupled_exp[condition]['data'].shape}, Shape Etichette: {new_all_th_concat_reconstructions_coupled_exp[condition]['labels'].shape}")
    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_th_concat_reconstructions_coupled_exp[condition]['labels'], return_counts = True)}")
    print()

In [ ]:
print(new_all_th_concat_reconstructions_coupled_exp.keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_th_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_th_resp']['labels'].shape)
print()
print(np.unique(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_th_resp']['labels'], return_counts = True))

In [ ]:
print(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_th_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_pt_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['baseline_vs_shared_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['th_resp_vs_pt_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['th_resp_vs_shared_resp'].keys())
print()
print(new_all_th_concat_reconstructions_coupled_exp['pt_resp_vs_shared_resp'].keys())

In [ ]:
'''ORA, QUELLO CHE INVECE CI SERVE CREARE, INVECE, 

SAREBBE LA VARIABILE CHE CONCATENA FRA TUTTI I SOGGETTI, I DATI E LE LABELS DELLA CHIAVE CHE IDENTIFICA
LA STESSA CONDIZIONE SPERIMENTALE SULLA QUALE STIAMO ITERANDO AL CICLO CORRENTE DEL FOR LOOP

SIA PER I DATI WAVELET, CHE PER I DATI 1-20!!!


Quindi, per ogni condizione sperimentale,
andiamo a concatenare tutti i dati e le etichette relativi a quella condizione,
ma provenienti da tutti i soggetti. 

Ogni condizione sperimentale ha già i dati e le etichette concatenati per ciascun soggetto,
e ora bisogna unire questi dati da tutti i soggetti per ogni condizione.

Immagina la struttura così:

Condizione sperimentale (per esempio, "condizione_1"):
Unire i dati di tutti i soggetti per la condizione "condizione_1".
Unire le etichette di tutti i soggetti per la condizione "condizione_1".


# La tua struttura dati originale 1_20
new_subject_level_concatenations_coupled_exp_th = {
    'subject_1': {
        'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
        'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        '
    'subject_2': {
        'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
        'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        
    subject_3': {
        'condition_1': {'data': np.array([1, 2, 3]), 'labels': np.array([0, 1, 0])},
        'condition_2': {'data': np.array([4, 5, 6]), 'labels': np.array([1, 0, 1])}
        },
        
    }
}


ATTENZIONE! SICCOME IO ITERO ANCHE RISPETTO AI LIVELLI DI RICOSTRUZIONE, 
LE CONCATENAZIONI VENGANO FATTE PER 3 VOLTE (1 PER CIASCUN LIVELLO)

MA QUESTO RISULTA OVVIAMENTE ERRATO! 

DI CONSEGUENZA, PER CALCOLARE LE LABELS PER OGNI CONDIZIONE SPERIMENTALE, 

SI FA RIFERIMENTO A     "new_all_th_concat_reconstructions_coupled_exp_1_20"

- SIA PER I LIVELLI WAVELET 
- SIA PER IL "LIVELLO" EEG FILTERED 1-20

QUESTO PERCHÉ OVVIAMENTE LE LABELS NON È CHE SI 'RADDOPPIANO' SOLO PER IL FATTO CHE STO CONSIDERANDO
DIVERSI LIVELLI DI RICOSTRUZIONE, MA È SOLO PER TESTARE LE DIFFERENTI PERFORMANCE DI CLASSIFICAZIONE 
RISPETTO AI LIVELLI WAVELET CHE CATTURANO CONTENUTI FREQUENTISTICI DIVERSI! (i.e., θ+δ, θ e δ)

'''

#PER I EEG FILTERED 1-20 Hz!

import numpy as np

# Nuovo dizionario per i risultati concatenati
new_all_pt_concat_reconstructions_coupled_exp_1_20 = {}

# Iteriamo attraverso tutti i soggetti e per ogni condizione
for subject, subject_data in new_subject_level_concatenations_coupled_exp_pt_1_20.items():
    
    for condition, data_labels in subject_data.items():
        
        # Se la condizione non esiste ancora nel dizionario finale, la inizializziamo
        if condition not in new_all_pt_concat_reconstructions_coupled_exp_1_20:
            new_all_pt_concat_reconstructions_coupled_exp_1_20[condition] = {
                'data': data_labels['data'],
                'labels': data_labels['labels']
            }
        else:
            # Concatenare i dati e le etichette per la condizione
            new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['data'] = np.concatenate(
                (new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['data'], data_labels['data'])
            )
            new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['labels'] = np.concatenate(
                (new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['labels'], data_labels['labels'])
            )

# Verifica dei risultati
#print("Dati concatenati per ciascuna condizione:")
#for condition in new_all_th_concat_reconstructions_coupled_exp_1_20:
#    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['data'].shape}, Shape Etichette: {new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['labels'].shape}")
#    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_th_concat_reconstructions_coupled_exp_1_20[condition]['labels'], return_counts = True)}")
#    print()

# Verifica dei risultati
print("Dati concatenati per ciascuna condizione:")
for condition in new_all_pt_concat_reconstructions_coupled_exp_1_20:
    print(f"\033[1m{condition}\033[0m - Shape Dati: {new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['data'].shape}, Shape Etichette: {new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['labels'].shape}")
    print(f"Conteggio Labels per \033[1m{condition}\033[0m: {np.unique(new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['labels'], return_counts=True)}")
    
    print(f"\n\033[4mShape delle etichette per ciascun soggetto nella condizione \033[1m{condition}\033[0m:\033[0m")
    for subject, subject_data in new_subject_level_concatenations_coupled_exp_pt_1_20.items():
        if condition in subject_data:
            subject_labels = subject_data[condition]['labels']
            print(f"- {subject}: {subject_labels.shape}")
    print()

In [ ]:
print(statistics_level_1_20.keys())
print(statistics_level_1_20['svm'].keys())
print(statistics_level_1_20['svm']['baseline_vs_th_resp'].keys())
print(statistics_level_1_20['svm']['baseline_vs_th_resp']['0-50'].keys())

In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW MEAN VERSION - DOMINIO DELLE FINESTRE

                                        ****UFFICIALE****

1) Cambio della funzione "calculate_chance_level" in modo che si salvi all'inizio,
un dizionario che tenga, per ciascuna condzione sperimentale, il chance level ottenuto


OUTPUT FINALE DI "chance_levels" sarebbe una cosa del tipo:

{
    'baseline_vs_th_resp': 0.85,
    'baseline_vs_pt_resp': 0.90,
    'baseline_vs_shared_resp': 0.80,
    'th_resp_vs_pt_resp': 0.88,
    'th_resp_vs_shared_resp': 0.89,
    'pt_resp_vs_shared_resp': 0.87
}


2) Successivamente, quando itera rispetto alla condizione sperimentale corrente, 

A) Verifica che se il nome stringa della chiave corrisponde a quella salvata nel dizionario
'chance_levels' 

B) Se è lo stesso, calcola il chance level rispetto a quella condizione sperimentale
 

Se stai eseguendo il codice con i dati per 

- statistics_level_1_20

Avrai un totale di 18 plots (6 per condizione mediata tra i soggetti di dati EEG!)

Ecco come si arriva a questo numero:

Se ci sono 6 condizioni sperimentali e 3 classificatori, allora il calcolo cambia. Ecco il nuovo scenario:

Hai 1 livello di dati EEG: preprocessed IIR filtered 1-20

In totale, ci sono 6 condizioni sperimentali.
Per ogni condizione, hai 3 classificatori (logistic_regression, xgboost, svm).

Quindi, il numero di plot sarà:

6 condizioni × 3  classificatori = 18 plots!


Quindi, in questo caso, il tuo codice genererà 54 plot totali, 
uno per ciascuna combinazione di classificatore, condizione e livello.

'''


import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)


# Definisci una mappa di colori per i classificatori
color_map = {
    'logistic_regression': 'green',
    'xgboost': 'purple',
    'svm': 'blue'
}


import numpy as np
import math

# Funzione per calcolare il livello di chance
def calculate_chance_level(new_all_pt_concat_reconstructions_coupled_exp_1_20):
    
    chance_levels = {}

    # Itera su tutte le chiavi principali
    for condition in new_all_pt_concat_reconstructions_coupled_exp_1_20.keys():
        print(f"\n\nChecking condition: \033[1m{condition}\033[0m")  # Diagnostica: stampa la condizione corrente
        
        # Verifica se la sottochiave 'labels' esiste per questa condizione
        if 'labels' in new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]:
            
            print(f"Labels found for condition: \033[1m{condition}\033[1m")  # Diagnostica: conferma che 'labels' esiste
            
            labels = new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['labels']  # Estrai le etichette

            # Calcolo il numero di occorrenze di ciascuna etichetta
            unique_values, labels_counts = np.unique(labels, return_counts=True)

            # Definisco il numero di fold
            num_folds = 5

            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1mAll Subjects\033[0m for Condition \033[1m{condition}\033[0m: {total_labels}")

            # Calcolo il numero di elementi di ogni fold
            elements_per_fold = total_labels / num_folds

            # Arrotondo il numero di elementi per fold
            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\nElements per Fold for \033[1m{condition}\033[0m: {rounded_elements_per_fold}")

            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            print(f"\nClass Percentage for \033[1m{condition}\033[0m: {class_percentage}")

            # Estraggo la percentuale della classe più grande
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{condition}\033[0m is: {highest_class_percentage}")

            # Calcolo il numero di campioni della classe più grande nel singolo fold (arrotondato per eccesso)
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
            print(f"\n\033[1mN° Samples for Highest Class for \033[1m{condition}\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1m{condition}\033[0m is: {exceeded_round_samples_for_highest_class}")

            # Calcolo del livello di chance per la classe più grande
            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{condition}\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            
            # Aggiungi il valore del livello di chance al dizionario per la condizione
            chance_levels[condition] = baseline_accuracy_highest_class_in_fold
            print(f"\nChance Level Accuracy for \033[1m{condition}\033[0m is: \033[1m{baseline_accuracy_highest_class_in_fold}\033[0m\n\n")
            
        else:
            # Se la sottochiave 'labels' non esiste, stampo un messaggio
            print(f"No labels found for condition: {condition}")
            
    # Restituisci il livello di chance calcolato
    return chance_levels
        
        
def plot_mean_best_scores_for_window(statistics_level_dict, level_str, save_path, coupled_exp_labels):
    
    chance_levels = calculate_chance_level(coupled_exp_labels)
    
    # Crea la cartella principale 'mean_wavelet_levels' dentro 'therapists'
    mean_wavelet_levels_path = os.path.join(save_path, 'mean_filtered_1_20_2_classes', 'patients')
    os.makedirs(mean_wavelet_levels_path, exist_ok=True)
    
    # Crea una lista per le finestre
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    '''
    Vado a crearmi delle strutture che mi appendano 
    per ogni classifier e condizione sperimentale, i vari valori, ossia la tripletta di 

    1) mean best score e 
    2) intervallo minore e 
    3) intervallo superiore dell'intervallo di confidenza
    
    per ciascuna delle finestre...
    '''
    
    # Inizializzo le medie per ogni classificatore, separati per condizione
    mean_scores = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
                   for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    ci_low = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
              for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    ci_high = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
               for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
    window_starts_samples = []
    window_ends_samples = []
    window_mid_points_samples = []

    # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
    start_sample = 0

    while start_sample + window_size_samples <= n_samples:
        end_sample = start_sample + window_size_samples
        window_starts_samples.append(start_sample)
        window_ends_samples.append(end_sample)
        window_mid_points_samples.append(start_sample + window_size_samples // 2)
        start_sample += stride_samples

    # Conversione dei punti in millisecondi
    window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
    window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
    window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    #print()
    #print(len(window_mid_points_in_ms))
    #print(len(window_ends_in_ms))
    #print(len(window_mid_points_in_ms))
    #print()
    
    # Numero di condizioni sperimentali
    conditions = list(statistics_level_dict['logistic_regression'].keys())
    
    # Itera su tutte le condizioni sperimentali
    for condition in conditions:
        
        plt.figure(figsize=(10, 7))

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''PER RAPPRESENTAZIONE IN DOMINIO FINESTRE'''

        # Imposta le etichette principali
        plt.xticks(tick_positions, window_labels)
        
        '''PER CAMBIO RAPPRESENTAZIONE DA DOMINIO FINESTRE A DOMINIO DEL TEMPO'''
        # Imposta le etichette principali
        #plt.xticks(tick_positions, window_labels)

        #plt.xticks(window_mid_points_in_ms, [f'{int(pos)} ms' for pos in window_mid_points_in_ms])


        # Stampa informativa
        print(f"\t\t\t\tProcessing condition: \033[1m{condition}\033[0m")
    

        # Aggiungi i punteggi medi dei classificatori e gli intervalli di confidenza per ogni condizione
        for classifier in ['logistic_regression', 'xgboost', 'svm']:

            if condition in statistics_level_dict[classifier].keys():
            
                #dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 
                #'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 
                #'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])
            
                #print(f"\nProcessing Classifier \033[1m{classifier}\033[0m for condition \033[1m{condition}\033[0m")
                
                #print(f"\nProcessing Classifier \033[1m{classifier}\033[0m")
                

                if condition in chance_levels:
                    baseline_accuracy_highest_class_in_fold = chance_levels[condition]

                    #print(f'Condition Chance Level for "\033[1m{condition}\033[0m" is: \033[1m{baseline_accuracy_highest_class_in_fold}\033[0m\n')
                
                # Itera sulle finestre e sui punti medi simultaneamente
                for window, mid_point in zip(n_windows, window_mid_points_in_ms):

                    # Recupera i dati relativi alla finestra corrente
                    window_data = statistics_level_dict[classifier][condition].get(window, None)
                    #print(f'\033[1mTaking Data\033[0m from Window \033[1m{window}\033[0m of Classifier \033[1m{classifier}\033[0m from Condition \033[1m{condition}\033[0m')
                    #print(f'{window_data}\n')
                    
                    if window_data:
                        #print(f"window_data['mean']: {window_data['mean']} (type: {type(window_data['mean'])})\n")
                        #print(f"mid_point: {mid_point} (type: {type(mid_point)})\n")

                        # Aggiungi i valori di media e CI intervals alle strutture dati che ho creato
                        #per ogni classifier
                        
                        #STEP 1: prelevo i valori

                        mean_best_score = window_data['mean']
                        ci_lower = window_data['ci_lower']
                        ci_upper = window_data['ci_upper']
                        
                        # STEP 2: Popolo le strutture con i valori medi e gli intervalli di confidenza
                        # rispetto al relativo classificatore e alla condizione sperimentale
                        # inserendolo rispetto all'indice della i-esima finestra
                        
                        #In questo modo, alla fine della iterazione sulle finestre, dovrei aver 
                        #per l'i-esimo classificatore e l'i-esima condizione sperimentale
                        
                        #TUTTI ED 11 I VALORI DI BEST SCORE E INTERVALLO INFERIORE/SUPERIORE 
                        #DELL'INTERVALLO DI CONFIDENZA!
                    
                        mean_scores[classifier][condition].append(mean_best_score)
                        ci_low[classifier][condition].append(ci_lower)
                        ci_high[classifier][condition].append(ci_upper)
                       
                        #print(f"For Classifier \033[1m{classifier}\033[0m we have:\n")
                        #print(f"\033[1mMean Best Score\033[0m for Window \033[1m{window}\033[0m:\n")
                        #print(mean_scores[classifier][condition])
                        #print(f"\nLower CI for Window \033[1m{window}\033[0m:\n")
                        #print(ci_low[classifier][condition])
                        #print(f"\nHigher CI for Window \033[1m{window}\033[0m:\n")
                        #print(ci_high[classifier][condition])
                        #print()
                        
                # Verifica la lunghezza delle liste
                if len(mean_scores[classifier][condition]) != len(window_mid_points_in_ms):
                    raise ValueError(f"La lunghezza di mean_scores ({len(mean_scores[classifier][condition])}) "
                                     f"non corrisponde a quella di window_mid_points_in_ms "
                                     f"({len(window_mid_points_in_ms)}) per {classifier} - {condition}.")
            
        for classifier in ['logistic_regression', 'xgboost', 'svm']: 
            # Genera il plot per il classificatore e la condizione corrente
            plt.plot(window_mid_points_in_ms, mean_scores[classifier][condition], 
                     label=f'{classifier}', color=color_map[classifier])

            plt.fill_between(window_mid_points_in_ms, ci_low[classifier][condition],
                             ci_high[classifier][condition], alpha=0.3, color=color_map[classifier])

        # Traccia la linea orizzontale del chance level
        if condition in chance_levels:
            plt.axhline(y=chance_levels[condition], color='red', linestyle='--', label=f'Chance Level ({condition})')

        # Linea verticale tratteggiata per il campione 50 (prestimolo)
        plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (50th sample)')
        
        # Aggiunge il livello di baseline in base al livello specificato
        if level_str == 'filtered_1_20':
            plt.title(f"Patients' Mean Best Accuracy Score for {condition} in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed 1-20 Hz")
        #elif level_str == '5':
        #    plt.title(f"Therapists'Mean Best Accuracy Score for {condition} in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level_str} - δ Range")
        #elif level_str == '5_detail':
        #    plt.title(f"Therapists'Mean Best Accuracy Score for {condition} in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level_str} - Θ Range")

        plt.xlabel('Windows (50 samples)', fontweight='bold')
        plt.ylabel('Mean Best Accuracy Score', fontweight='bold')

        plt.legend(loc='best')
        plt.grid(True)

        
        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'mean_best_scores_all_pts_level_{level_str}_{condition}_window_domain.png' 
        save_file_path = os.path.join(save_path, 'mean_filtered_1_20_2_classes', 'patients', filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[0m\n')
    
                
save_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_2_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/'

plot_mean_best_scores_for_window(statistics_level_1_20, 'filtered_1_20', save_path, new_all_pt_concat_reconstructions_coupled_exp_1_20)


In [ ]:
'''PLOTS FINALI DELLE MEDIE CON INTERVALLI DI CONFIDENZA - NEW MEAN VERSION - DOMINIO DEL TEMPO

                                        ****UFFICIALE****

1) Cambio della funzione "calculate_chance_level" in modo che si salvi all'inizio,
un dizionario che tenga, per ciascuna condzione sperimentale, il chance level ottenuto


OUTPUT FINALE DI "chance_levels" sarebbe una cosa del tipo:

{
    'baseline_vs_th_resp': 0.85,
    'baseline_vs_pt_resp': 0.90,
    'baseline_vs_shared_resp': 0.80,
    'th_resp_vs_pt_resp': 0.88,
    'th_resp_vs_shared_resp': 0.89,
    'pt_resp_vs_shared_resp': 0.87
}


2) Successivamente, quando itera rispetto alla condizione sperimentale corrente, 

A) Verifica che se il nome stringa della chiave corrisponde a quella salvata nel dizionario
'chance_levels' 

B) Se è lo stesso, calcola il chance level rispetto a quella condizione sperimentale
 

Se stai eseguendo il codice con i dati per 

- statistics_level_1_20

Avrai un totale di 18 plots (6 per condizione mediata tra i soggetti di dati EEG!)

Ecco come si arriva a questo numero:

Se ci sono 6 condizioni sperimentali e 3 classificatori, allora il calcolo cambia. Ecco il nuovo scenario:

Hai 1 livello di dati EEG: preprocessed IIR filtered 1-20

In totale, ci sono 6 condizioni sperimentali.
Per ogni condizione, hai 3 classificatori (logistic_regression, xgboost, svm).

Quindi, il numero di plot sarà:

6 condizioni × 3  classificatori = 18 plots!


Quindi, in questo caso, il tuo codice genererà 54 plot totali, 
uno per ciascuna combinazione di classificatore, condizione e livello.

'''


import numpy as np
import matplotlib.pyplot as plt
import os
import math

# Parametri generali
sampling_rate = 250  # Hz
total_time = 1200  # ms
n_samples = 300  # Numero totale di campioni
window_size_samples = 50  # Dimensione della finestra in campioni
stride_samples = 25  # Sovrapposizione della finestra in campioni

time_in_ms = np.arange(-200, total_time - 200, 1000 / sampling_rate)


# Definisci una mappa di colori per i classificatori
color_map = {
    'logistic_regression': 'green',
    'xgboost': 'purple',
    'svm': 'blue'
}


import numpy as np
import math

# Funzione per calcolare il livello di chance
def calculate_chance_level(new_all_pt_concat_reconstructions_coupled_exp_1_20):
    
    chance_levels = {}

    # Itera su tutte le chiavi principali
    for condition in new_all_pt_concat_reconstructions_coupled_exp_1_20.keys():
        print(f"\n\nChecking condition: \033[1m{condition}\033[0m")  # Diagnostica: stampa la condizione corrente
        
        # Verifica se la sottochiave 'labels' esiste per questa condizione
        if 'labels' in new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]:
            
            print(f"Labels found for condition: \033[1m{condition}\033[1m")  # Diagnostica: conferma che 'labels' esiste
            
            labels = new_all_pt_concat_reconstructions_coupled_exp_1_20[condition]['labels']  # Estrai le etichette

            # Calcolo il numero di occorrenze di ciascuna etichetta
            unique_values, labels_counts = np.unique(labels, return_counts=True)

            # Definisco il numero di fold
            num_folds = 5

            total_labels = np.sum(labels_counts)
            print(f"\nTot Labels for \033[1mAll Subjects\033[0m for Condition \033[1m{condition}\033[0m: {total_labels}")

            # Calcolo il numero di elementi di ogni fold
            elements_per_fold = total_labels / num_folds

            # Arrotondo il numero di elementi per fold
            rounded_elements_per_fold = math.floor(elements_per_fold)
            print(f"\nElements per Fold for \033[1m{condition}\033[0m: {rounded_elements_per_fold}")

            # Calcola la percentuale di ciascuna classe
            class_percentage = labels_counts / total_labels * 100
            print(f"\nClass Percentage for \033[1m{condition}\033[0m: {class_percentage}")

            # Estraggo la percentuale della classe più grande
            highest_class_percentage = max(class_percentage)
            print(f"\n\033[1mHighest Class Percentage\033[0m for \033[1m{condition}\033[0m is: {highest_class_percentage}")

            # Calcolo il numero di campioni della classe più grande nel singolo fold (arrotondato per eccesso)
            samples_for_highest_class = rounded_elements_per_fold * (highest_class_percentage / 100)
            print(f"\n\033[1mN° Samples for Highest Class for \033[1m{condition}\033[0m is: {samples_for_highest_class}")

            exceeded_round_samples_for_highest_class = math.ceil(samples_for_highest_class)
            print(f"\n\033[1mN° Exceeded Samples for Highest Class for \033[1m{condition}\033[0m is: {exceeded_round_samples_for_highest_class}")

            # Calcolo del livello di chance per la classe più grande
            baseline_accuracy_highest_class_in_fold = exceeded_round_samples_for_highest_class / rounded_elements_per_fold
            print(f"\n\033[1mChance Level Accuracy for Highest Class in Each Fold for \033[1m{condition}\033[0m is: {baseline_accuracy_highest_class_in_fold}")
            
            # Aggiungi il valore del livello di chance al dizionario per la condizione
            chance_levels[condition] = baseline_accuracy_highest_class_in_fold
            print(f"\nChance Level Accuracy for \033[1m{condition}\033[0m is: \033[1m{baseline_accuracy_highest_class_in_fold}\033[0m\n\n")
            
        else:
            # Se la sottochiave 'labels' non esiste, stampo un messaggio
            print(f"No labels found for condition: {condition}")
            
    # Restituisci il livello di chance calcolato
    return chance_levels
        
        
def plot_mean_best_scores_for_window(statistics_level_dict, level_str, save_path, coupled_exp_labels):
    
    chance_levels = calculate_chance_level(coupled_exp_labels)
    
    # Crea la cartella principale 'mean_wavelet_levels' dentro 'therapists'
    mean_wavelet_levels_path = os.path.join(save_path, 'mean_filtered_1_20_2_classes', 'therapists')
    os.makedirs(mean_wavelet_levels_path, exist_ok=True)
    
    # Crea una lista per le finestre
    n_windows = ["0-50", "25-75", "50-100", "75-125", "100-150", "125-175", 
                 "150-200", "175-225", "200-250", "225-275", "250-300"]
    
    '''
    Vado a crearmi delle strutture che mi appendano 
    per ogni classifier e condizione sperimentale, i vari valori, ossia la tripletta di 

    1) mean best score e 
    2) intervallo minore e 
    3) intervallo superiore dell'intervallo di confidenza
    
    per ciascuna delle finestre...
    '''
    
    # Inizializzo le medie per ogni classificatore, separati per condizione
    mean_scores = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
                   for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    ci_low = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
              for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    ci_high = {classifier: {condition: [] for condition in statistics_level_dict[classifier].keys()} 
               for classifier in ['logistic_regression', 'xgboost', 'svm']}
    
    # Inizializzo i contenitori degli inizi e le fine delle finestre in campioni discretizzati EEG
    window_starts_samples = []
    window_ends_samples = []
    window_mid_points_samples = []

    # Calcolo dinamicamente gli inizi e le fine delle finestre in campioni discretizzati EEG 
    start_sample = 0

    while start_sample + window_size_samples <= n_samples:
        end_sample = start_sample + window_size_samples
        window_starts_samples.append(start_sample)
        window_ends_samples.append(end_sample)
        window_mid_points_samples.append(start_sample + window_size_samples // 2)
        start_sample += stride_samples

    # Conversione dei punti in millisecondi
    window_starts_in_ms = [time_in_ms[start] for start in window_starts_samples if start < len(time_in_ms)]
    window_ends_in_ms = [time_in_ms[end] for end in window_ends_samples if end < len(time_in_ms)]
    window_mid_points_in_ms = [time_in_ms[mid] for mid in window_mid_points_samples if mid < len(time_in_ms)]

    #print()
    #print(len(window_mid_points_in_ms))
    #print(len(window_ends_in_ms))
    #print(len(window_mid_points_in_ms))
    #print()
    
    # Numero di condizioni sperimentali
    conditions = list(statistics_level_dict['logistic_regression'].keys())
    
    # Itera su tutte le condizioni sperimentali
    for condition in conditions:
        
        plt.figure(figsize=(10, 7))

        # Creiamo le etichette per le finestre
        window_labels = [f'Win {i+1}' for i in range(len(window_mid_points_in_ms))]
        tick_positions = window_mid_points_in_ms

        '''PER RAPPRESENTAZIONE IN DOMINIO FINESTRE'''

        # Imposta le etichette principali
        #plt.xticks(tick_positions, window_labels)
        
        '''PER CAMBIO RAPPRESENTAZIONE DA DOMINIO FINESTRE A DOMINIO DEL TEMPO'''
        # Imposta le etichette principali
        #plt.xticks(tick_positions, window_labels)

        plt.xticks(window_mid_points_in_ms, [f'{int(pos)}' for pos in window_mid_points_in_ms])


        # Stampa informativa
        print(f"\t\t\t\tProcessing condition: \033[1m{condition}\033[0m")
    

        # Aggiungi i punteggi medi dei classificatori e gli intervalli di confidenza per ogni condizione
        for classifier in ['logistic_regression', 'xgboost', 'svm']:

            if condition in statistics_level_dict[classifier].keys():
            
                #dict_keys(['baseline_vs_th_resp', 'baseline_vs_pt_resp', 
                #'baseline_vs_shared_resp', 'th_resp_vs_pt_resp', 
                #'th_resp_vs_shared_resp', 'pt_resp_vs_shared_resp'])
            
                #print(f"\nProcessing Classifier \033[1m{classifier}\033[0m for condition \033[1m{condition}\033[0m")
                
                #print(f"\nProcessing Classifier \033[1m{classifier}\033[0m")
                

                if condition in chance_levels:
                    baseline_accuracy_highest_class_in_fold = chance_levels[condition]

                    #print(f'Condition Chance Level for "\033[1m{condition}\033[0m" is: \033[1m{baseline_accuracy_highest_class_in_fold}\033[0m\n')
                
                # Itera sulle finestre e sui punti medi simultaneamente
                for window, mid_point in zip(n_windows, window_mid_points_in_ms):

                    # Recupera i dati relativi alla finestra corrente
                    window_data = statistics_level_dict[classifier][condition].get(window, None)
                    #print(f'\033[1mTaking Data\033[0m from Window \033[1m{window}\033[0m of Classifier \033[1m{classifier}\033[0m from Condition \033[1m{condition}\033[0m')
                    #print(f'{window_data}\n')
                    
                    if window_data:
                        #print(f"window_data['mean']: {window_data['mean']} (type: {type(window_data['mean'])})\n")
                        #print(f"mid_point: {mid_point} (type: {type(mid_point)})\n")

                        # Aggiungi i valori di media e CI intervals alle strutture dati che ho creato
                        #per ogni classifier
                        
                        #STEP 1: prelevo i valori

                        mean_best_score = window_data['mean']
                        ci_lower = window_data['ci_lower']
                        ci_upper = window_data['ci_upper']
                        
                        # STEP 2: Popolo le strutture con i valori medi e gli intervalli di confidenza
                        # rispetto al relativo classificatore e alla condizione sperimentale
                        # inserendolo rispetto all'indice della i-esima finestra
                        
                        #In questo modo, alla fine della iterazione sulle finestre, dovrei aver 
                        #per l'i-esimo classificatore e l'i-esima condizione sperimentale
                        
                        #TUTTI ED 11 I VALORI DI BEST SCORE E INTERVALLO INFERIORE/SUPERIORE 
                        #DELL'INTERVALLO DI CONFIDENZA!
                    
                        mean_scores[classifier][condition].append(mean_best_score)
                        ci_low[classifier][condition].append(ci_lower)
                        ci_high[classifier][condition].append(ci_upper)
                       
                        #print(f"For Classifier \033[1m{classifier}\033[0m we have:\n")
                        #print(f"\033[1mMean Best Score\033[0m for Window \033[1m{window}\033[0m:\n")
                        #print(mean_scores[classifier][condition])
                        #print(f"\nLower CI for Window \033[1m{window}\033[0m:\n")
                        #print(ci_low[classifier][condition])
                        #print(f"\nHigher CI for Window \033[1m{window}\033[0m:\n")
                        #print(ci_high[classifier][condition])
                        #print()
                        
                # Verifica la lunghezza delle liste
                if len(mean_scores[classifier][condition]) != len(window_mid_points_in_ms):
                    raise ValueError(f"La lunghezza di mean_scores ({len(mean_scores[classifier][condition])}) "
                                     f"non corrisponde a quella di window_mid_points_in_ms "
                                     f"({len(window_mid_points_in_ms)}) per {classifier} - {condition}.")
            
        for classifier in ['logistic_regression', 'xgboost', 'svm']: 
            # Genera il plot per il classificatore e la condizione corrente
            plt.plot(window_mid_points_in_ms, mean_scores[classifier][condition], 
                     label=f'{classifier}', color=color_map[classifier])

            plt.fill_between(window_mid_points_in_ms, ci_low[classifier][condition],
                             ci_high[classifier][condition], alpha=0.3, color=color_map[classifier])

        # Traccia la linea orizzontale del chance level
        if condition in chance_levels:
            plt.axhline(y=chance_levels[condition], color='red', linestyle='--', label=f'Chance Level ({condition})')

        # Linea verticale tratteggiata per il campione 50 (prestimolo)
        plt.axvline(x=time_in_ms[50], color='black', linestyle='--', label='End of Prestimulus (0 mms)')
        
        # Aggiunge il livello di baseline in base al livello specificato
        if level_str == 'filtered_1_20':
            plt.title(f"Patients' Mean Best Accuracy Score for {condition} in Win $i^{{th}}$ (Size: 50, Stride: 25) - EEG Preprocessed 1-20 Hz")
        #elif level_str == '5':
        #    plt.title(f"Therapists'Mean Best Accuracy Score for {condition} in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level_str} - δ Range")
        #elif level_str == '5_detail':
        #    plt.title(f"Therapists'Mean Best Accuracy Score for {condition} in Win $i^{{th}}$ (Size: 50, Stride: 25) - Level {level_str} - Θ Range")

        plt.xlabel('Time (mms)', fontweight='bold')
        plt.ylabel('Mean Best Accuracy Score', fontweight='bold')

        plt.legend(loc='best')
        plt.grid(True)

        
        #plt.show()

        # Salva il plot nel percorso specifico
        filename = f'mean_best_scores_all_pts_level_{level_str}_{condition}_time_domain.png' 
        save_file_path = os.path.join(save_path, 'mean_filtered_1_20_2_classes', 'patients', filename)
        plt.savefig(save_file_path, bbox_inches='tight')
        plt.close()
        print(f'Plot salvato in: \n\033[1m{save_file_path}\033[0m\n')
    
                
save_path = '/home/stefano/Interrogait/New_Plots_Sliding_Estimator_MNE/all_classifiers_plots/EEG_2_classes_1_20Hz/EEG_50_window_25_overlap_coupled_exp_cond/'

plot_mean_best_scores_for_window(statistics_level_1_20, 'filtered_1_20', save_path, new_all_pt_concat_reconstructions_coupled_exp_1_20)